A cute little demo showing the simplest usage of minGPT. Configured to run fine on Macbook Air in like a minute.

In [ ]:
classdef EQCOMDupireSpotGFPricingVolGrid < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        numOfFactors
        
        %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFPricingVolGrid(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;
                
                eqCOMDupireSpotGF.pricingForwardGrid = {};
                eqCOMDupireSpotGF.pricingReducedForwardGrid = {};
                eqCOMDupireSpotGF.pricingVolGrid = {};
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            try
                fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            catch ME
                aaa = 0;
            end
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    aaa =1.0;
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end   
                
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1));
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            % we use the same linear interpolation scheme as calibration
            useVolProxyInterpolationYN = 'YES';
            if strcmp(useVolProxyInterpolationYN,'YES')
                
                for ii =1:length(x)
                    localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
                end
            else
                volKnotPoints = zeros(length(ipos),1);
                for i=1: length(ipos)
                    volKnotPoints(i) = Ks(ipos(i));
                end


                for i=1:length(x)
                    xIdx = find(volKnotPoints <=x(i));
                    if isempty(xIdx)
                        localVol(i) = localVolLine(1);
                    elseif max(xIdx) == ipos(length(ipos))
                        localVol(i) = localVolLine(length(ipos));
                    else
                        localVolIdx = max(xIdx);
                        weight = (x(i)-Ks(ipos(localVolIdx)))/(Ks(ipos(localVolIdx)+1)-Ks(ipos(localVolIdx)));
                        localVol(i) = weight*localVolLine(ipos(localVolIdx)+1)+(1-weight)*localVolLine(ipos(localVolIdx));
                    end
                end
            end
            
        end
        
        function localVol = InterpolateLocalVolPricingVolGrid(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            localVolLineGrid = eqCOMDupireSpotGF.pricingVolGrid{idxNow};
            forwardGrid =      eqCOMDupireSpotGF.pricingReducedForwardGrid{idxNow};
            
            localVol =  zeros(length(x),1);
            for ii =1:length(x)
                localVol(ii) = H_interpolation(forwardGrid,localVolLineGrid,x(ii),1);
            end
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U,Ks)
            
            NMC = length(lastX);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U)
            
            NMC = length(lastX);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPricingVolGrid(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVolPricingVolGrid(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPricingVolGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)

            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNMs = zeros(size(expiry));
            for i=1:length(fwdNMs)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            pricingVolGrid = cell(size(volProxy,1),1);
            pricingForwardGrid = cell(size(volProxy,1),1);
            pricingReducedForwardGrid = cell(size(volProxy,1),1);
            pricingVolGridSize = cell(size(volProxy,1),1);
            dy = 0.05;
            for i=1:size(volProxy,1)
%                 volATM = volProxy(i,round(size(volProxy,2)+1)/2);
                volATM = impVolSurf(i,round(size(volProxy,2)+1)/2);
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
%                 X_max = max(1.3*fwdNM(i),basePrice*exp(5.0*volATM*sqrt(expiry(i)/365.0)));
%                 X_min = min(0.7*fwdNM(i),basePrice*exp(-5.0*volATM*sqrt(expiry(i)/365.0)));
                
                X_max = basePrice*exp(5.0*volATM*sqrt(expiry(i)/365.0));
                X_min = basePrice*exp(-5.0*volATM*sqrt(expiry(i)/365.0));
                
                K = round(log(X_max/X_min)/0.05);
                temp_pricingForwardGrid = zeros(1,K+1);
                temp_pricingReducedForwardGrid = zeros(1,K+1);
                temp_pricingVolGrid = zeros(1,K+1);
                
                pricingVolGridSize{i} = K+1;
                for j=1:K+1
                      temp_pricingForwardGrid(j) = X_min*exp((j-1)*dy);
                      temp_pricingReducedForwardGrid(j) = temp_pricingForwardGrid(j)/fwdNM(i);
                      temp_pricingVolGrid(j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(j),1);
                end
                
                pricingForwardGrid{i} = temp_pricingForwardGrid;
                pricingReducedForwardGrid{i} = temp_pricingReducedForwardGrid;
                pricingVolGrid{i} = temp_pricingVolGrid;
                
            end
            
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    mcmcOut   = inductMCForwardNewPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 40000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = unhitValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           dummyMeshB = zeros(length(timeStep),2);
           dummyIdx = 1;
           dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
           dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
           dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                    %apply american option
                    comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValueB  = meshB/onePayoffD;
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    if strcmp(vanillaParams.params('callPutFlag'),'C')
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
                            if payoffStateB.cashflow(j) > contiValueB(j)
                                ccc = 1.0;
                            end
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                        
                    else
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                    end
                    payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
                    meshB = payoffStateB.cashflow_npv;
                    dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
                    dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
                    dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = europeanValue.payoff(Pricingidx);
           americanValue.npv = americanValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            
            initX = ones(NMC,1);
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                nextX = eqCOMDupireSpotGF.inductMCForward(timeStep(i-1),timeStep(i),startIdx,endIdx,timeScheduleInfo,nextX,dZStep,params);
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            initX = ones(NMC,1);
            initXIdx = ones(NMC,1)*params.Pricingidx;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            nextXIdx = initXIdx;
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextX,nextXIdx,U(:,i-1),Ks);
                nextX = mcmcOut.nextX;
                nextXIdx = mcmcOut.nextXIdx;
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
            newTimeSchedule = sort(union(volExpiry,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
            MCTimeStep = length(expiry); % -1 because 0

            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            
            
          %% Solve  Forward PDE(GF) One time
            outGF = eqCOMDupireSpotGF.Solve1DGF(tvar,mkt_dT,optParams.dK,optParams.lastProb,optParams);
            
            newProb = outGF.newProb;
            optParams.meshProb = newProb;
           %% PDE(GF) Solve End
           % find the implied vol of dupire model
           if strcmp(eqCOMDupireSpotGF.modelParams('UseLetsBeRational'),'YES')
               target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           else
               target = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           end
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,dT,lastProb,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.fwdMoneyness(idxNow,i);
            end
                
%             if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
%                 % market strike points in fwd PDE grid
%                 fwdFactor = eqCOMDupireSpotGF.FwdFactor(params.expiry(idxNow));
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i)/fwdFactor;
%                 end
%             else
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i);
%                 end
%             end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastProb = lastProb;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;
            
            if idxNow <= numOfCutoffTenor
                lowerIdx = min(find(optParams.marketStrikes >= lowerCutoff));
                upperIdx = max(find(optParams.marketStrikes <= upperCutoff));
            end
            
            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
%             tol = 0.0001;
%             maxIter = 1000;
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
            out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            bootStrapOut.lastProb = out.newProb;
            bootStrapOut.condProb = out.condProb;
            
        end
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            if strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess')
                for k=1:expirySize
    %                 fwd = black.Fwd(spot,expiry(k));
    %                 df = black.zeroCurve.DF(expiry(k)/365.0);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize

                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        if strike(j) <= 0
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        else
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        end

                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'P');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'C');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        end
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                         
                    end
                    dfOut(k) = black.zeroCurve.DF(expiry(k)/365.0);
                end
                
            end
                
%             if strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         fwdStrike = strike(j)/fwdFactor;
%                         if fwdStrike <= 1.0
% %                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                         else
% %                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                             blackOTMPrices(k,j)  = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                             
%                         end
%                     end
%                 end
%             else
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         if strike(j) <= 1
%                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                         else
%                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                         end
%                     end
%                 end
%             end
%             
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
            params.fwdMoneyness = fwdMoneyness;
            
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            
            %initialze the intial probability distribution in the grid
            initProb = zeros(1,params.Ns);
            initProb(params.Pricingidx) = 1.0;
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;
            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
%                     toc
                    
%                     tic
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    params.marketStrikes = out.marketStrikes;
                    
%                     toc
                    
%                     calculate backward scheme for given target
%                     compareforwardMCFlag = 1 for one step euler scheme
%                     compareforwardMCFlag = 2 for daily euler scheme
%                     
%                     compareforwardMCFlag = 3 for markov chain monte carlo
                     
                    
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
  
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end

%                     toc
                case 'bootstrapForward'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    % compute implied surface for targetStrikes;
                    targetExpiry = params.expiry;
                    
                    %% at T call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVol = outDummy.impVolSurface;
                    out.cValueSurface = outDummy.cValueSurface;
                    out.pValueSurface = outDummy.pValueSurface;
                    out.probMeshInt = outDummy.probMeshInt;
                    
                     %% at T-dT call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0.000001;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVolPrev = outDummy.impVolSurface;
                    out.cValueSurfacePrev = outDummy.cValueSurface;
                    out.pValueSurfacePrev = outDummy.pValueSurface;
                    out.probMeshIntPrev = outDummy.probMeshInt;
                    
                    aaa = 1.0;
                    
                case 'bootstrapForwardOnly'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    aaa = 1.0;
                    
                    
                      

                otherwise
                    disp('unImplemented')
                    
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNormalSSR2FQuanto < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        numOfFactors
        
        slope
        
        % 2factors model params
        rho
        alpha
        beta
        
        % dummy params for global alpha,beta,rho, sigma_flat calibration
        % form ATM vol strips
        
        sigma_flat
        sigma_Short
        sigma_Long
        
        futuresStates
        
        %quantoCorrection
        quantoFXVol
        quantoCorr
        atmForwardVol
        
        atmForwardVolNew
        quantoFXVolNew
        sigmaTimes
        
%        %% pricingVolGrid data
%         pricingForwardGrid
%         pricingReducedForwardGrid
%         pricingVolGrid
%         pricingVolGridSize
%         volNodeFwdCurve
%         modelStatesFixedGrid
%         basePrice

        % SSR output info
        targetStrikes
        
        %fixedStrike    
        settleFuturesRef
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        slopeTerm
        
        gridType
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNormalSSR2FQuanto(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
              
                if isKey(EQModel.modelParams,'gridType')
                    eqCOMDupireSpotGF.gridType = EQModel.modelParams('gridType');
                else
                    eqCOMDupireSpotGF.gridType = 'uniform';
                end
                
                if isKey(EQModel.modelParams,'settleFutures')
                    eqCOMDupireSpotGF.settleFutures = EQModel.modelParams('settleFutures');
                else
                    eqCOMDupireSpotGF.settleFutures = [];
                end
                
                if isKey(EQModel.modelParams,'settleFuturesRef')
                    eqCOMDupireSpotGF.settleFuturesRef = EQModel.modelParams('settleFuturesRef');
                else
                    eqCOMDupireSpotGF.settleFuturesRef = [];
                end
                
              %% 2F model Params
                eqCOMDupireSpotGF.rho   = EQModel.modelParams('rho');
                eqCOMDupireSpotGF.alpha = EQModel.modelParams('alpha');
                eqCOMDupireSpotGF.beta  = EQModel.modelParams('beta');
                
                if isKey(EQModel.modelParams,'sigma_flat')
                    eqCOMDupireSpotGF.sigma_flat = EQModel.modelParams('sigma_flat');
                else
                    eqCOMDupireSpotGF.sigma_flat = 0.2;
                end
                
                if isKey(EQModel.modelParams,'sigma_Short')
                    eqCOMDupireSpotGF.sigma_Short = EQModel.modelParams('sigma_Short');
                else
                    eqCOMDupireSpotGF.sigma_Short = 0.2;
                end
                
                if isKey(EQModel.modelParams,'sigma_Long')
                    eqCOMDupireSpotGF.sigma_Long = EQModel.modelParams('sigma_Long');
                else
                    eqCOMDupireSpotGF.sigma_Long = 0.2;
                end
                
                if isKey(EQModel.modelParams,'quantoFXVol')
                    eqCOMDupireSpotGF.quantoFXVol = EQModel.modelParams('quantoFXVol');
                else
                    eqCOMDupireSpotGF.quantoFXVol = [0  0.0];
                end
                
                if isKey(EQModel.modelParams,'quantoCorr')
                    eqCOMDupireSpotGF.quantoCorr = EQModel.modelParams('quantoCorr');
                else
                    eqCOMDupireSpotGF.quantoCorr = 0.0;
                end
                
                if isKey(EQModel.modelParams,'atmForwardVol')
                    eqCOMDupireSpotGF.atmForwardVol = EQModel.modelParams('atmForwardVol');
                else
                    eqCOMDupireSpotGF.atmForwardVol = [];
                end
                
                if isKey(EQModel.modelParams,'atmForwardVolNew')
                    eqCOMDupireSpotGF.atmForwardVolNew = EQModel.modelParams('atmForwardVolNew');
                else
                    eqCOMDupireSpotGF.atmForwardVolNew = [];
                end
                
                if isKey(EQModel.modelParams,'quantoFXVolNew')
                    eqCOMDupireSpotGF.quantoFXVolNew = EQModel.modelParams('quantoFXVolNew');
                else
                    eqCOMDupireSpotGF.quantoFXVolNew = [];
                end
                
                if isKey(EQModel.modelParams,'sigmaTimes')
                    eqCOMDupireSpotGF.sigmaTimes = EQModel.modelParams('sigmaTimes');
                else
                    eqCOMDupireSpotGF.sigmaTimes = [];
                end
              %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% reducedFuturesNMonths
                if ~isKey(eqCOMDupireSpotGF.modelParams,'reducedFuturesNMonths')
                    dummyReferenceFutures = eqCOMDupireSpotGF.modelParams('reducedFutures');
                    dummyReferenceFuturesNMonths = zeros(size(dummyReferenceFutures,1),3);
                    dummyReferenceFuturesNMonths(:,1) = dummyReferenceFutures(:,1);
                    dummyReferenceFuturesNMonths(:,2) = dummyReferenceFutures(:,1);
                    dummyReferenceFuturesNMonths(:,3) = dummyReferenceFutures(:,2);
                    eqCOMDupireSpotGF.modelParams('reducedFuturesNMonths') = dummyReferenceFuturesNMonths;
                end
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 2 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 2;
                
                eqCOMDupireSpotGF.futuresStates = [];

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)
            settleFuture_idxNow  = eqCOMDupireSpotGF.settleFutures(idxNow);
            localVol = zeros(length(Ks),1);
            KsNew = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            try
                fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            catch ME
                aaa = 0;
            end
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    for i=1:length(volProxy)
                        volProxyKs(i) = fwdMoneynessPerExpiry(i);
                    end

                    for i=1:length(Ks)
                        localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),3);
                    end   
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end
                
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneynessExtrapLinear')
                for i=1:length(volProxy)
                    volProxyKs(i) = settleFuture_idxNow + fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(KsNew)
                    KsNew(i) = settleFuture_idxNow + Ks(i);
                end
                
                dummyOut = interp1ExtrapLinear(volProxyKs,volProxy,KsNew','linear');
                localVol = dummyOut';
                
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneynessRightExtrapLinear')
                for i=1:length(volProxy)
                    volProxyKs(i) = settleFuture_idxNow +fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(KsNew)
                    KsNew(i) = settleFuture_idxNow + Ks(i);
                end
                
                dummyOut = interp1LeftFlatExtrapNew(volProxyKs,volProxy,KsNew','linear');
                localVol = dummyOut';
                    
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            Ks = optParams.params.Ks;
            if strcmp(eqCOMDupireSpotGF.gridType,'uniform')
                dK2 = dK*dK;
                for i=1:size
                    a(i) = -0.5*dT*proxy(i)*proxy(i)/dK2;
                    b(i) = 1 + dT*proxy(i)*proxy(i)/dK2;
                    b_rg(i) = dT*proxy(i)*proxy(i)/dK2;
                    c(i) = -0.5*dT*proxy(i)*proxy(i)/dK2;
                end
            else
                
                for i=2:size-1
                    dK_i = Ks(i)-Ks(i-1);
                    dK_i1 = Ks(i+1)-Ks(i);
                    
                    a(i) = -0.5*dT*proxy(i)*proxy(i)/dK_i/(dK_i + dK_i1)*2.0;
                    b(i) = 1 + 0.5*dT*proxy(i)*proxy(i)/dK_i/dK_i1*2.0;
                    b_rg(i) = 0.5*dT*proxy(i)*proxy(i)/dK_i/dK_i1*2.0;
                    c(i) = -0.5*dT*proxy(i)*proxy(i)/dK_i1/(dK_i + dK_i1)*2.0;
                end
            end
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
%                 a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
%                 b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
%                 b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
%                 c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                
                a(i) = -0.5*dT*proxy(i)*proxy(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1));
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            settleFuture_idxNow  = eqCOMDupireSpotGF.settleFutures(idxNow);
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            y = zeros(length(x),1);
            fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            volProxyKs = zeros(1,length(volProxy));
            % we use the same linear interpolation scheme as calibration
            useVolProxyInterpolationYN = 'YES';
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
           
                dummyOut = interp1FlatExtrapNew(fwdMoneynessPerExpiry,volProxy,x','linear');
                localVol = dummyOut';
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneynessExtrapLinear')
                volProxyKs = settleFuture_idxNow + fwdMoneynessPerExpiry;
                y = settleFuture_idxNow + x;
                dummyOut = interp1ExtrapLinear(volProxyKs,volProxy,y','linear');
                localVol = dummyOut';
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneynessRightExtrapLinear')
                volProxyKs = settleFuture_idxNow + fwdMoneynessPerExpiry;
                y = settleFuture_idxNow + x;
                dummyOut = interp1LeftFlatExtrapNew(volProxyKs,volProxy,y','linear');
                localVol = dummyOut';
                
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
%                 for ii =1:length(x)
%                     localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),3);
%                 end
                dummyOut = interp1FlatExtrapNew(fwdMoneynessPerExpiry,volProxy,x','pchip');
                localVol = dummyOut';
                
                
            else
                volKnotPoints = zeros(length(ipos),1);
                for i=1: length(ipos)
                    volKnotPoints(i) = Ks(ipos(i));
                end


                for i=1:length(x)
                    xIdx = find(volKnotPoints <=x(i));
                    if isempty(xIdx)
                        localVol(i) = localVolLine(1);
                    elseif max(xIdx) == ipos(length(ipos))
                        localVol(i) = localVolLine(length(ipos));
                    else
                        localVolIdx = max(xIdx);
                        weight = (x(i)-Ks(ipos(localVolIdx)))/(Ks(ipos(localVolIdx)+1)-Ks(ipos(localVolIdx)));
                        localVol(i) = weight*localVolLine(ipos(localVolIdx)+1)+(1-weight)*localVolLine(ipos(localVolIdx));
                    end
                end
            end
            
        end
        
        function localVol = InterpolateLocalVol_Square(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            % we use the same linear interpolation scheme as calibration
            useVolProxyInterpolationYN = 'YES';
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                
%                 for ii =1:length(x)
%                     localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
%                 end
%               
                volProxy2 = volProxy.*volProxy; 
                dummyOut2 = interp1FlatExtrapNew(fwdMoneynessPerExpiry,volProxy2,x','linear');
                dummyOut = sqrt(dummyOut2);
                localVol = dummyOut';
                
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
%                 for ii =1:length(x)
%                     localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),3);
%                 end
                dummyOut = interp1FlatExtrapNew(fwdMoneynessPerExpiry,volProxy,x','pchip');
                localVol = dummyOut';
                
                
            else
                volKnotPoints = zeros(length(ipos),1);
                for i=1: length(ipos)
                    volKnotPoints(i) = Ks(ipos(i));
                end


                for i=1:length(x)
                    xIdx = find(volKnotPoints <=x(i));
                    if isempty(xIdx)
                        localVol(i) = localVolLine(1);
                    elseif max(xIdx) == ipos(length(ipos))
                        localVol(i) = localVolLine(length(ipos));
                    else
                        localVolIdx = max(xIdx);
                        weight = (x(i)-Ks(ipos(localVolIdx)))/(Ks(ipos(localVolIdx)+1)-Ks(ipos(localVolIdx)));
                        localVol(i) = weight*localVolLine(ipos(localVolIdx)+1)+(1-weight)*localVolLine(ipos(localVolIdx));
                    end
                end
            end
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U,Ks)
            
            NMC = length(lastX);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U)
            
            NMC = length(lastX);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j)+0.01);
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
%                     predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1));
                    predictor(i) = predictor(i) + localVol(i)*sqrtDt*dZ(i,j-startIdx+1); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function newX = inductMCForwardTest(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j)+0.01);
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
%                     predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1));
                    predictor(i) = predictor(i) + localVol(i)*sqrtDt*dZ(i,j-startIdx+1); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = computeLongShortVolModelVol(eqCOMDupireSpotGF,toD,futuresExpiry)
            
            sigma_Short = eqCOMDupireSpotGF.sigma_Short;
            sigma_Long  = eqCOMDupireSpotGF.sigma_Long;
            
            rho = eqCOMDupireSpotGF.rho;
            
            alpha = sigma_Short/sigma_Long;
            
            beta = eqCOMDupireSpotGF.beta;
            
            To = toD/365.0;
            
            Tf = futuresExpiry/365.0;
            
            totalVariance = sigma_Long*sigma_Long*(1.0 + 2.0*rho*alpha*exp(-beta*Tf)*1.0/(beta)*(exp(beta*To)-1.0) + ...
                            alpha*alpha*exp(-2.0*beta*Tf)*1.0/(2.0*beta)*(exp(2.0*beta*To)-1.0));
                        
            out = sqrt(totalVariance/To);
        end
        
        function out = computeSkewFlatModelVol(eqCOMDupireSpotGF,toD,futuresExpiry)
            
            sigma_flat = eqCOMDupireSpotGF.sigma_flat;
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            To = toD/365.0;
            
            Tf = futuresExpiry/365.0;
            
            totalVariance = sigma_flat*sigma_flat*(1.0 + 2.0*rho*alpha*exp(-beta*Tf)*1.0/(beta)*(exp(beta*To)-1.0) + ...
                            alpha*alpha*exp(-2.0*beta*Tf)*1.0/(2.0*beta)*(exp(2.0*beta*To)-1.0));
                        
            out = sqrt(totalVariance/To);
        end
        
        function out = computeFuturesCorr(eqCOMDupireSpotGF,observationTime,forwardMaturity1,forwardMaturity2)
            % 2factor modelParams
            if abs(forwardMaturity2-3.0) < 0.01
                aaa = 1.0;
            end
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            tau1 = (forwardMaturity1 - observationTime);
            tau2 = (forwardMaturity2 - observationTime);
            
            P11 = sqrt(1-rho*rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau1)+alpha*alpha*exp(-2.0*beta*tau1));
            P12 = (alpha*exp(-beta*tau1)+rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau1)+alpha*alpha*exp(-2.0*beta*tau1));
            
            P21 = sqrt(1-rho*rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau2)+alpha*alpha*exp(-2.0*beta*tau2));
            P22 = (alpha*exp(-beta*tau2)+rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau2)+alpha*alpha*exp(-2.0*beta*tau2));
            
            out = P11*P21 + P12*P22;
            
        end
        
        function out = LoadingDParams(eqCOMDupireSpotGF,observationTime,forwardMaturities,modelParams1)
            % 2factor modelParams
            if abs(forwardMaturities(end)-3.0) < 0.01
                aaa = 1.0;
            end
            
            out = zeros(length(forwardMaturities),2);
            
            rho = modelParams1.rho;
            alpha = modelParams1.alpha;
            beta = modelParams1.beta;
                        
            for idxhh=1:length(forwardMaturities)
                tau1 = (forwardMaturities(idxhh) - observationTime);

                P11 = sqrt(1-rho*rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau1)+alpha*alpha*exp(-2.0*beta*tau1));
                P12 = (alpha*exp(-beta*tau1)+rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau1)+alpha*alpha*exp(-2.0*beta*tau1));
                out(idxhh,1) = P11;
                out(idxhh,2) = P12;
                
            end
            
            
        end
        
        function out = LoadingD(eqCOMDupireSpotGF,observationTime,forwardMaturities)
            % 2factor modelParams
            if abs(forwardMaturities(end)-3.0) < 0.01
                aaa = 1.0;
            end
            
            out = zeros(length(forwardMaturities),2);
            
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            for idxhh=1:length(forwardMaturities)
                tau1 = (forwardMaturities(idxhh) - observationTime);

                P11 = sqrt(1-rho*rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau1)+alpha*alpha*exp(-2.0*beta*tau1));
                P12 = (alpha*exp(-beta*tau1)+rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau1)+alpha*alpha*exp(-2.0*beta*tau1));
                out(idxhh,1) = P11;
                out(idxhh,2) = P12;
                
            end
            
            
        end
        
        function out = computeFuturesInterCurveCorr(eqCOMDupireSpotGF,observationTime,forwardMaturity1,forwardMaturity2,...
                                                    modelParams1,modelParams2)
            % 2factor modelParams
            if abs(forwardMaturity2-3.0) < 0.01
                aaa = 1.0;
            end
            
            rho1 = modelParams1.rho;
            alpha1 = modelParams1.alpha;
            beta1 = modelParams1.beta;
            
            rho2 = modelParams2.rho;
            alpha2 = modelParams2.alpha;
            beta2 = modelParams2.beta;
            
            tau1 = (forwardMaturity1 - observationTime);
            tau2 = (forwardMaturity2 - observationTime);
            
            P11 = sqrt(1-rho1*rho1)/sqrt(1+2.0*rho1*alpha1*exp(-beta1*tau1)+alpha1*alpha1*exp(-2.0*beta1*tau1));
            P12 = (alpha1*exp(-beta1*tau1)+rho1)/sqrt(1+2.0*rho1*alpha1*exp(-beta1*tau1)+alpha1*alpha1*exp(-2.0*beta1*tau1));
            
            P21 = sqrt(1-rho2*rho2)/sqrt(1+2.0*rho2*alpha2*exp(-beta2*tau2)+alpha2*alpha2*exp(-2.0*beta2*tau2));
            P22 = (alpha2*exp(-beta2*tau2)+rho2)/sqrt(1+2.0*rho2*alpha2*exp(-beta2*tau2)+alpha2*alpha2*exp(-2.0*beta2*tau2));
            
            out = P11*P21 + P12*P22;
            
        end
        
        function out = computeFuturesCorr2(eqCOMDupireSpotGF,observationTime,forwardMaturity1,forwardMaturity2)
            % 2factor modelParams
            if abs(forwardMaturity2-3.0) < 0.01
                aaa = 1.0;
            end
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            tau1 = (forwardMaturity1 - observationTime);
            tau2 = (forwardMaturity2 - observationTime);
            
            denom1 = sqrt(1+2.0*rho*alpha*exp(-beta*tau1)+alpha*alpha*exp(-2.0*beta*tau1));
            denom2 = sqrt(1+2.0*rho*alpha*exp(-beta*tau2)+alpha*alpha*exp(-2.0*beta*tau2));
            numerator = 1+rho*alpha*(exp(-beta*tau1)+exp(-beta*tau2))+alpha*alpha*exp(-beta*(tau1+tau2));
            
            out = numerator/denom1/denom2;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastFuturesStates,dZ,dW)
            
            predictor = lastFuturesStates;
            corrector = lastFuturesStates;
            
            % find to-be alive futures for the diffusion time period
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(toTime <= forwardMaturity);
            if isempty(idx)
               idxNM = forwardCurveSize;
            else
               idxNM = min(idx);
            end
            
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            modelStateSize = size(predictor,1);
            
            % 2factor modelParams
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            for idxR=idxNM:forwardCurveSize
                tau = (forwardMaturity(idxR) - fromTime)/365.0;
                P1 = sqrt((1-rho*rho)/(1+2.0*eqCOMDupireSpotGF.rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau)));
%                 P2 = sqrt(1-P1*P1);
                P2 = (alpha*exp(-beta*tau)+rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau));
                
                % targetX = F(t,T_r)/F(0,T_r)
                targetX = predictor(:,idxR)/forwardCurve(idxR,2);
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(targetX,fromTime + 0.01);
                
                for i=1:modelStateSize
                    corrector(i,idxR) = predictor(i,idxR)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*(P1*dZ(i)+P2*dW(i))); 
                end
            end
            
            mcmcOut.nextFuturesStates = corrector;
            
        end
        
        function mcmcOut = inductMCForwardNewReduced(eqCOMDupireSpotGF,fromTime,toTime,lastFuturesStates,dZ0)
            
            predictor = lastFuturesStates;
            corrector = lastFuturesStates;
            
            % need to generalized with the numOfFactors ?
            dZ = dZ0(:,1);
            dW = dZ0(:,2);
            
            % find to-be alive futures for the diffusion time period
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            
            forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
            
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(toTime <= forwardMaturity);
            if isempty(idx)
               idxNM = forwardCurveSize;
            else
               idxNM = min(idx);
            end
            
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            modelStateSize = size(predictor,1);
            
            % 2factor modelParams
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            for idxR=idxNM:forwardCurveSize
                tau = (forwardMaturity(idxR) - fromTime)/365.0;
                P1 = sqrt((1-rho*rho)/(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau)));
%                 P2 = sqrt(1-P1*P1);
                P2 = (alpha*exp(-beta*tau)+rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau));
                
                % targetX = F(t,T_r)/F(0,T_r)
                targetX = predictor(:,idxR)/forwardCurve(idxR,2);
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(targetX,fromTime + 0.01);
                
                for i=1:modelStateSize
                    corrector(i,idxR) = predictor(i,idxR)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*(P1*dZ(i)+P2*dW(i))); 
                end
            end
            
            mcmcOut.nextFuturesStates = corrector;
            mcmcOut.idxNM = idxNM;
            
            if strcmp(eqCOMDupireSpotGF.modelParams('computeRealizedCorrelationYN'),'true')
                % realized correlation
                nextX1 = corrector(:,idxNM);
                
                lastX1 = predictor(:,idxNM);
                
                
                deltaX1 = log(nextX1./lastX1);
                
                % in - curve correl
                aa = corrector(:,idxNM:end);
                aa0 = predictor(:,idxNM:end);
                deltaA = log(aa./aa0);
                aa_size = size(aa,2);
                
                inCurveCorrA = zeros(aa_size,aa_size); 
                inCurveCovA  = zeros(aa_size,aa_size);
                for ii=1:aa_size
                    for jj=1:aa_size
                        inCurveCorrA(ii,jj) = corr(deltaA(:,ii),deltaA(:,jj));
                        dummyCovA  =  cov(deltaA(:,ii),deltaA(:,jj));
                        inCurveCovA(ii,jj)  =  dummyCovA(1,2);
                        
                    end
                end
                
                
              %% correlation between projected co-ordiates(parallel & flattening)
               futuresSize = size(aa,2);
               e1 = ones(futuresSize,1);
               deltaE2 = 1.0/(futuresSize-1);
               e2=0.0:deltaE2:1.0;
               e2 = e2';
               e2 = e2 - mean(e2)*ones(futuresSize,1);
               e2 = e2*-1.0;
               
               cordPar = zeros(size(aa,1),1);
               cordFlat =zeros(size(aa,1),1);
               dF = aa- aa0;
               normE1 = e1'*e1; 
               normE2 = e2'*e2; 
               cordPar = (dF*e1)/normE1;
               cordFlat = (dF*e2)/normE2;
               inCurveCorrB = corr(cordPar,cordFlat);
                %% Correlation Between Calendar Spread And Futures
%                 
%                 % 1st 4 is log normal return's corr
%                 % 4~ last is RS Spread
%                 deltaB = zeros(size(aa));
%                 
%                 for jj=1:size(aa,2)
%                     if jj <= 4 + 1 - idxNM
%                         for ii=1:size(aa,1)
%                             deltaB(ii,jj) = log(aa(ii,jj)/aa0(ii,jj));
%                         end
%                     else
%                         for ii=1:size(aa,1)
%                             deltaB(ii,jj) = (aa(ii,jj)- aa(ii,jj-1)) - (aa0(ii,jj) - aa0(ii,jj-1));
%                         end
%                     end
%                 end
%                 
%                 inCurveCorrB = zeros(aa_size,aa_size);
%                 inCurveCovB = zeros(aa_size,aa_size); 
%                 
%                 for ii=1:aa_size
%                     for jj=1:aa_size
%                         inCurveCorrB(ii,jj) = corr(deltaB(:,ii),deltaB(:,jj));
%                         dummyCovB  =  cov(deltaA(:,ii),deltaA(:,jj));
%                         inCurveCovB(ii,jj)  =  dummyCovB(1,2);
%                         
%                     end
%                 end
%                 
                %curve-curve correl
                corrInfo.inCurveCorrA = inCurveCorrA;
                corrInfo.inCurveCorrB = inCurveCorrB;
                
                corrInfo.inCurveCovA = inCurveCovA;
%                 corrInfo.inCurveCovB = inCurveCovB;
                
                corrInfo.cordPar = cordPar;
                corrInfo.cordFlat = cordFlat;
                
                mcmcOut.corrInfo = corrInfo;
            end
            
        end
        
        function mcmcOut = inductMCForwardNewReducedQuanto(eqCOMDupireSpotGF,fromTime,toTime,lastFuturesStates,dZ0)
            
            predictor = lastFuturesStates;
            corrector = lastFuturesStates;
            
            % need to generalized with the numOfFactors ?
            dZ = dZ0(:,1);
            dW = dZ0(:,2);
            
            % quantoCorrection
            quantoFXVol = eqCOMDupireSpotGF.modelParams('quantoFXVol');
            quantoCorr = eqCOMDupireSpotGF.modelParams('quantoCorr');
            
            quantoMaturity = quantoFXVol(:,1);
            quantoSize = size(quantoMaturity,1);
            idxQ = find(toTime <= quantoMaturity);
            if isempty(idxQ)
               idxQuanto = quantoSize;
            else
               idxQuanto = min(idxQ);
            end
            
            quantoFxVol1 = quantoFXVol(idxQuanto,2);
            
            quantoDrift = -1.0*quantoFxVol1*quantoCorr;
            
            % find to-be alive futures for the diffusion time period
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            
            forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
            
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(toTime <= forwardMaturity);
            if isempty(idx)
               idxNM = forwardCurveSize;
            else
               idxNM = min(idx);
            end
            
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            modelStateSize = size(predictor,1);
            
            % 2factor modelParams
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            for idxR=idxNM:forwardCurveSize
                tau = (forwardMaturity(idxR) - fromTime)/365.0;
                P1 = sqrt((1-rho*rho)/(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau)));
%                 P2 = sqrt(1-P1*P1);
                P2 = (alpha*exp(-beta*tau)+rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau));
                
                % targetX = F(t,T_r) - F(0,T_r)
                targetX = predictor(:,idxR) -forwardCurve(idxR,2);
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(targetX,fromTime + 0.01);
                
                for i=1:modelStateSize
%                     corrector(i,idxR) = predictor(i,idxR)*exp(-0.5*localVol(i)*localVol(i)*Dt+quantoDrift*localVol(i)*Dt + localVol(i)*sqrtDt*(P1*dZ(i)+P2*dW(i)));
                    corrector(i,idxR) = predictor(i,idxR) + quantoDrift*localVol(i)*Dt + localVol(i)*sqrtDt*(P1*dZ(i)+P2*dW(i));
                end
            end
            
            mcmcOut.nextFuturesStates = corrector;
            mcmcOut.idxNM = idxNM;
            
            if strcmp(eqCOMDupireSpotGF.modelParams('computeRealizedCorrelationYN'),'true')
                % realized correlation
                nextX1 = corrector(:,idxNM);
                
                lastX1 = predictor(:,idxNM);
                
                
%                 deltaX1 = log(nextX1./lastX1);
                deltaX1 = nextX1 - lastX1;
                
                % in - curve correl
                aa = corrector(:,idxNM:end);
                aa0 = predictor(:,idxNM:end);
%                 deltaA = log(aa./aa0);
                deltaA = aa - aa0;
                
                aa_size = size(aa,2);
                
                inCurveCorrA = zeros(aa_size,aa_size); 
                inCurveCovA  = zeros(aa_size,aa_size);
                for ii=1:aa_size
                    for jj=1:aa_size
                        inCurveCorrA(ii,jj) = corr(deltaA(:,ii),deltaA(:,jj));
                        dummyCovA  =  cov(deltaA(:,ii),deltaA(:,jj));
                        inCurveCovA(ii,jj)  =  dummyCovA(1,2);
                        
                    end
                end
                
                
              %% correlation between projected co-ordiates(parallel & flattening)
               futuresSize = size(aa,2);
               e1 = ones(futuresSize,1);
               deltaE2 = 1.0/(futuresSize-1);
               e2=0.0:deltaE2:1.0;
               e2 = e2';
               e2 = e2 - mean(e2)*ones(futuresSize,1);
               e2 = e2*-1.0;
               
               cordPar = zeros(size(aa,1),1);
               cordFlat =zeros(size(aa,1),1);
               dF = aa- aa0;
               normE1 = e1'*e1; 
               normE2 = e2'*e2; 
               cordPar = (dF*e1)/normE1;
               cordFlat = (dF*e2)/normE2;
               inCurveCorrB = corr(cordPar,cordFlat);
                %% Correlation Between Calendar Spread And Futures
%                 
%                 % 1st 4 is log normal return's corr
%                 % 4~ last is RS Spread
%                 deltaB = zeros(size(aa));
%                 
%                 for jj=1:size(aa,2)
%                     if jj <= 4 + 1 - idxNM
%                         for ii=1:size(aa,1)
%                             deltaB(ii,jj) = log(aa(ii,jj)/aa0(ii,jj));
%                         end
%                     else
%                         for ii=1:size(aa,1)
%                             deltaB(ii,jj) = (aa(ii,jj)- aa(ii,jj-1)) - (aa0(ii,jj) - aa0(ii,jj-1));
%                         end
%                     end
%                 end
%                 
%                 inCurveCorrB = zeros(aa_size,aa_size);
%                 inCurveCovB = zeros(aa_size,aa_size); 
%                 
%                 for ii=1:aa_size
%                     for jj=1:aa_size
%                         inCurveCorrB(ii,jj) = corr(deltaB(:,ii),deltaB(:,jj));
%                         dummyCovB  =  cov(deltaA(:,ii),deltaA(:,jj));
%                         inCurveCovB(ii,jj)  =  dummyCovB(1,2);
%                         
%                     end
%                 end
%                 
                %curve-curve correl
                corrInfo.inCurveCorrA = inCurveCorrA;
                corrInfo.inCurveCorrB = inCurveCorrB;
                
                corrInfo.inCurveCovA = inCurveCovA;
%                 corrInfo.inCurveCovB = inCurveCovB;
                
                corrInfo.cordPar = cordPar;
                corrInfo.cordFlat = cordFlat;
                
                mcmcOut.corrInfo = corrInfo;
            end
            
        end
        
        function mcmcOut = inductMCForwardNewReducedNMonthsQuanto(eqCOMDupireSpotGF,fromTime,toTime,lastFuturesStates,dZ0)
            
            predictor = lastFuturesStates;
            corrector = lastFuturesStates;
            
            % need to generalized with the numOfFactors ?
            dZ = dZ0(:,1);
            dW = dZ0(:,2);
            
            % quantoCorrection
            quantoFXVol = eqCOMDupireSpotGF.modelParams('quantoFXVol');
            quantoCorr = eqCOMDupireSpotGF.modelParams('quantoCorr');
            
            quantoMaturity = quantoFXVol(:,1);
            quantoSize = size(quantoMaturity,1);
            idxQ = find(toTime <= quantoMaturity);
            if isempty(idxQ)
               idxQuanto = quantoSize;
            else
               idxQuanto = min(idxQ);
            end
            
            quantoFxVol1 = quantoFXVol(idxQuanto,2);
            
            quantoDrift = -1.0*quantoFxVol1*quantoCorr;
            
            % find to-be alive futures for the diffusion time period
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            
%             forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
            forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFuturesNMonths');
            
            forwardCurveSize = size(forwardCurve,1);
            forwardNMonthsMaturity = forwardCurve(:,1);
            forwardMaturity = forwardCurve(:,2);
            
            % filtering with NMonthsMaturity
            idx = find(toTime <= forwardNMonthsMaturity);
            if isempty(idx)
               idxNM = forwardCurveSize;
            else
               idxNM = min(idx);
            end
            
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            modelStateSize = size(predictor,1);
            
            % 2factor modelParams
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            for idxR=idxNM:forwardCurveSize
                tau = (forwardMaturity(idxR) - fromTime)/365.0;
                P1 = sqrt((1-rho*rho)/(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau)));
%                 P2 = sqrt(1-P1*P1);
                P2 = (alpha*exp(-beta*tau)+rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau));
                
                % targetX = F(t,T_r)/F(0,T_r)
%                 targetX = predictor(:,idxR)/forwardCurve(idxR,3);
                targetX = predictor(:,idxR) - forwardCurve(idxR,3);
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(targetX,fromTime + 0.01);
                
                for i=1:modelStateSize
%                     corrector(i,idxR) = predictor(i,idxR)*exp(-0.5*localVol(i)*localVol(i)*Dt+quantoDrift*localVol(i)*Dt + localVol(i)*sqrtDt*(P1*dZ(i)+P2*dW(i))); 
                    corrector(i,idxR) = predictor(i,idxR) + quantoDrift*localVol(i)*Dt + localVol(i)*sqrtDt*(P1*dZ(i)+P2*dW(i));
                end
            end
            
            mcmcOut.nextFuturesStates = corrector;
            mcmcOut.idxNM = idxNM;
            
            if strcmp(eqCOMDupireSpotGF.modelParams('computeRealizedCorrelationYN'),'true')
                % realized correlation
                nextX1 = corrector(:,idxNM);
                
                lastX1 = predictor(:,idxNM);
                
                
%                 deltaX1 = log(nextX1./lastX1);
                deltaX1 = nextX1 - lastX1;
                
                % in - curve correl
                aa = corrector(:,idxNM:end);
                aa0 = predictor(:,idxNM:end);
%                 deltaA = log(aa./aa0);
                deltaA = aa - aa0;
                
                aa_size = size(aa,2);
                
                inCurveCorrA = zeros(aa_size,aa_size); 
                inCurveCovA  = zeros(aa_size,aa_size);
                for ii=1:aa_size
                    for jj=1:aa_size
                        inCurveCorrA(ii,jj) = corr(deltaA(:,ii),deltaA(:,jj));
                        dummyCovA  =  cov(deltaA(:,ii),deltaA(:,jj));
                        inCurveCovA(ii,jj)  =  dummyCovA(1,2);
                        
                    end
                end
                
                
              %% correlation between projected co-ordiates(parallel & flattening)
               futuresSize = size(aa,2);
               e1 = ones(futuresSize,1);
               deltaE2 = 1.0/(futuresSize-1);
               e2=0.0:deltaE2:1.0;
               e2 = e2';
               e2 = e2 - mean(e2)*ones(futuresSize,1);
               e2 = e2*-1.0;
               
               cordPar = zeros(size(aa,1),1);
               cordFlat =zeros(size(aa,1),1);
               dF = aa- aa0;
               normE1 = e1'*e1; 
               normE2 = e2'*e2; 
               cordPar = (dF*e1)/normE1;
               cordFlat = (dF*e2)/normE2;
               inCurveCorrB = corr(cordPar,cordFlat);
                %% Correlation Between Calendar Spread And Futures
%                 
%                 % 1st 4 is log normal return's corr
%                 % 4~ last is RS Spread
%                 deltaB = zeros(size(aa));
%                 
%                 for jj=1:size(aa,2)
%                     if jj <= 4 + 1 - idxNM
%                         for ii=1:size(aa,1)
%                             deltaB(ii,jj) = log(aa(ii,jj)/aa0(ii,jj));
%                         end
%                     else
%                         for ii=1:size(aa,1)
%                             deltaB(ii,jj) = (aa(ii,jj)- aa(ii,jj-1)) - (aa0(ii,jj) - aa0(ii,jj-1));
%                         end
%                     end
%                 end
%                 
%                 inCurveCorrB = zeros(aa_size,aa_size);
%                 inCurveCovB = zeros(aa_size,aa_size); 
%                 
%                 for ii=1:aa_size
%                     for jj=1:aa_size
%                         inCurveCorrB(ii,jj) = corr(deltaB(:,ii),deltaB(:,jj));
%                         dummyCovB  =  cov(deltaA(:,ii),deltaA(:,jj));
%                         inCurveCovB(ii,jj)  =  dummyCovB(1,2);
%                         
%                     end
%                 end
%                 
                %curve-curve correl
                corrInfo.inCurveCorrA = inCurveCorrA;
                corrInfo.inCurveCorrB = inCurveCorrB;
                
                corrInfo.inCurveCovA = inCurveCovA;
%                 corrInfo.inCurveCovB = inCurveCovB;
                
                corrInfo.cordPar = cordPar;
                corrInfo.cordFlat = cordFlat;
                
                mcmcOut.corrInfo = corrInfo;
            end
            
        end
        
        function mcmcOut = inductMCForwardNewReducedQuanto_Square(eqCOMDupireSpotGF,fromTime,toTime,lastFuturesStates,dZ0)
            
            predictor = lastFuturesStates;
            corrector = lastFuturesStates;
            
            % need to generalized with the numOfFactors ?
            dZ = dZ0(:,1);
            dW = dZ0(:,2);
            
            % quantoCorrection
            quantoFXVol = eqCOMDupireSpotGF.modelParams('quantoFXVol');
            quantoCorr = eqCOMDupireSpotGF.modelParams('quantoCorr');
            
            quantoMaturity = quantoFXVol(:,1);
            quantoSize = size(quantoMaturity,1);
            idxQ = find(toTime <= quantoMaturity);
            if isempty(idxQ)
               idxQuanto = quantoSize;
            else
               idxQuanto = min(idxQ);
            end
            
            quantoFxVol1 = quantoFXVol(idxQuanto,2);
            
            quantoDrift = -1.0*quantoFxVol1*quantoCorr;
            
            % find to-be alive futures for the diffusion time period
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            
            forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
            
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(toTime <= forwardMaturity);
            if isempty(idx)
               idxNM = forwardCurveSize;
            else
               idxNM = min(idx);
            end
            
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            modelStateSize = size(predictor,1);
            
            % 2factor modelParams
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            for idxR=idxNM:forwardCurveSize
                tau = (forwardMaturity(idxR) - fromTime)/365.0;
                P1 = sqrt((1-rho*rho)/(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau)));
%                 P2 = sqrt(1-P1*P1);
                P2 = (alpha*exp(-beta*tau)+rho)/sqrt(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau));
                
                % targetX = F(t,T_r)/F(0,T_r)
                targetX = predictor(:,idxR)/forwardCurve(idxR,2);
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol_Square(targetX,fromTime + 0.01);
                
                for i=1:modelStateSize
                    corrector(i,idxR) = predictor(i,idxR)*exp(-0.5*localVol(i)*localVol(i)*Dt+quantoDrift*localVol(i)*Dt + localVol(i)*sqrtDt*(P1*dZ(i)+P2*dW(i))); 
                end
            end
            
            mcmcOut.nextFuturesStates = corrector;
            mcmcOut.idxNM = idxNM;
            
            if strcmp(eqCOMDupireSpotGF.modelParams('computeRealizedCorrelationYN'),'true')
                % realized correlation
                nextX1 = corrector(:,idxNM);
                
                lastX1 = predictor(:,idxNM);
                
                
                deltaX1 = log(nextX1./lastX1);
                
                % in - curve correl
                aa = corrector(:,idxNM:end);
                aa0 = predictor(:,idxNM:end);
                deltaA = log(aa./aa0);
                aa_size = size(aa,2);
                
                inCurveCorrA = zeros(aa_size,aa_size); 
                inCurveCovA  = zeros(aa_size,aa_size);
                for ii=1:aa_size
                    for jj=1:aa_size
                        inCurveCorrA(ii,jj) = corr(deltaA(:,ii),deltaA(:,jj));
                        dummyCovA  =  cov(deltaA(:,ii),deltaA(:,jj));
                        inCurveCovA(ii,jj)  =  dummyCovA(1,2);
                        
                    end
                end
                
                
              %% correlation between projected co-ordiates(parallel & flattening)
               futuresSize = size(aa,2);
               e1 = ones(futuresSize,1);
               deltaE2 = 1.0/(futuresSize-1);
               e2=0.0:deltaE2:1.0;
               e2 = e2';
               e2 = e2 - mean(e2)*ones(futuresSize,1);
               e2 = e2*-1.0;
               
               cordPar = zeros(size(aa,1),1);
               cordFlat =zeros(size(aa,1),1);
               dF = aa- aa0;
               normE1 = e1'*e1; 
               normE2 = e2'*e2; 
               cordPar = (dF*e1)/normE1;
               cordFlat = (dF*e2)/normE2;
               inCurveCorrB = corr(cordPar,cordFlat);
                %% Correlation Between Calendar Spread And Futures
%                 
%                 % 1st 4 is log normal return's corr
%                 % 4~ last is RS Spread
%                 deltaB = zeros(size(aa));
%                 
%                 for jj=1:size(aa,2)
%                     if jj <= 4 + 1 - idxNM
%                         for ii=1:size(aa,1)
%                             deltaB(ii,jj) = log(aa(ii,jj)/aa0(ii,jj));
%                         end
%                     else
%                         for ii=1:size(aa,1)
%                             deltaB(ii,jj) = (aa(ii,jj)- aa(ii,jj-1)) - (aa0(ii,jj) - aa0(ii,jj-1));
%                         end
%                     end
%                 end
%                 
%                 inCurveCorrB = zeros(aa_size,aa_size);
%                 inCurveCovB = zeros(aa_size,aa_size); 
%                 
%                 for ii=1:aa_size
%                     for jj=1:aa_size
%                         inCurveCorrB(ii,jj) = corr(deltaB(:,ii),deltaB(:,jj));
%                         dummyCovB  =  cov(deltaA(:,ii),deltaA(:,jj));
%                         inCurveCovB(ii,jj)  =  dummyCovB(1,2);
%                         
%                     end
%                 end
%                 
                %curve-curve correl
                corrInfo.inCurveCorrA = inCurveCorrA;
                corrInfo.inCurveCorrB = inCurveCorrB;
                
                corrInfo.inCurveCovA = inCurveCovA;
%                 corrInfo.inCurveCovB = inCurveCovB;
                
                corrInfo.cordPar = cordPar;
                corrInfo.cordFlat = cordFlat;
                
                mcmcOut.corrInfo = corrInfo;
            end
            
        end
        
        function mcmcOut = inductMCForwardNewInterp(eqCOMDupireSpotGF,fromTime,toTime,lastFuturesStates,dZ,dW)
            
            predictor = lastFuturesStates;
            corrector = lastFuturesStates;
            
            % find to-be alive futures for the diffusion time period
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            
            forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
            
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(toTime <= forwardMaturity);
            if isempty(idx)
               idxNM = forwardCurveSize;
            else
               idxNM = min(idx);
            end
            
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            modelStateSize = size(predictor,1);
            
            % 2factor modelParams
            rho = eqCOMDupireSpotGF.rho;
            alpha = eqCOMDupireSpotGF.alpha;
            beta = eqCOMDupireSpotGF.beta;
            
            for idxR=idxNM:forwardCurveSize
                tau = (forwardMaturity(idxR) - fromTime)/365.0;
                P1 = sqrt((1-rho*rho)/(1+2.0*rho*alpha*exp(-beta*tau)+alpha*alpha*exp(-2.0*beta*tau)));
                P2 = sqrt(1-P1*P1);
                
                % targetX = F(t,T_r)/F(0,T_r)
                targetX = predictor(:,idxR)/forwardCurve(idxR,2);
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(targetX,fromTime + 0.01);
                
                for i=1:modelStateSize
                    corrector(i,idxR) = predictor(i,idxR)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*(P1*dZ(i)+P2*dW(i))); 
                end
            end
            
            mcmcOut.nextFuturesStates = corrector;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 1000;
            Tol = 1e-10;
            MaxIter = 10000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 0.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
%                      out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter);
                     out.vols(i) = BisecNormIV('P',0.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
%                      out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
%                                                 NormalVanillaFwd(txDay,fwd,fwdStrike,sig,CPFlag)
                     out.interpBlackPrices(i) = NormalVanillaFwd(params.params.expiry(idxNow),0.0,K,out.vols(i),'P');
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
%                     out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter);
                    out.vols(i) = BisecNormIV('C',0.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
%                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                    out.interpBlackPrices(i) = NormalVanillaFwd(params.params.expiry(idxNow),0.0,K,out.vols(i),'C');
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 0.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,futuresStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
%              stateSize = length(modelStates);
%              stateSize = size(modelStates,2);
             
%              stochasticFwd = zeros(stateSize,1);
             
             stochasticFwd = futuresStates(:,idxNM);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = futuresStates(idxNM,i); 
%              end
             
             out = stochasticFwd;
        end
        
        function out = DetATMQuantoAdj(eqCOMDupireSpotGF,observeTime)
            % quantoCorrection
             quantoFXVolNew = eqCOMDupireSpotGF.quantoFXVolNew;
             quantoCorr  = eqCOMDupireSpotGF.quantoCorr;
             atmForwardVolNew = eqCOMDupireSpotGF.atmForwardVolNew;
             
             
             sigmaTimes = eqCOMDupireSpotGF.atmForwardVolNew;
             
             sigmaSize = length(sigmaTimes);
             
             from = 0.0;
             to = observeTime;
             
             for i=1:sigmaSize
                if to<= sigmaTimes(i)
                    break;
                end
             end
             
             endIdx = i;
            
             sigmaValue1 = quantoFXVolNew(:,2);
             sigmaValue2 = atmForwardVolNew(:,2);
             corr = quantoCorr;
             
             
             lastU  = 0.0;
             
             quantoAdj= 0;
             for i=1:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
                quantoAdj = quantoAdj + -1.0*corr*sig1*sig2*(U-lastU)/365.0;
                lastU = U;
             end
             
             expQuantoAdj = exp(quantoAdj);
             out = expQuantoAdj;
             
        end
        
        function out = CommoFwdNMQuantoAdj(eqCOMDupireSpotGF,observeTime)
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             fwd_NM = forwardCurve(idxNM,2);
             expQuantoAdj = eqCOMDupireSpotGF.DetATMQuantoAdj(observeTime);
             out.value = fwd_NM * expQuantoAdj;
             out.quantoAdjFactor = expQuantoAdj;
             
%              % quantoCorrection
%              quantoFXVolNew = eqCOMDupireSpotGF.quantoFXVolNew;
%              quantoCorr  = eqCOMDupireSpotGF.quantoCorr;
%              atmForwardVolNew = eqCOMDupireSpotGF.atmForwardVolNew;
%              
%              
%              sigmaTimes = eqCOMDupireSpotGF.atmForwardVolNew;
%              
%              sigmaSize = length(sigmaTimes);
%              
%              from = 0.0;
%              to = observeTime;
%              
%              for i=1:sigmaSize
%                 if to<= sigmaTimes(i)
%                     break;
%                 end
%              end
%              
%              endIdx = i;
%             
%              sigmaValue1 = quantoFXVolNew(:,2);
%              sigmaValue2 = atmForwardVolNew(:,2);
%              corr = quantoCorr;
%              
%              
%              lastU  = 0.0;
%              
%              quantoAdj= 0;
%              for i=1:endIdx
%                 if (i< endIdx) U = sigmaTimes(i);else U = to;end;
%                 if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
%                 if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
%                 quantoAdj = quantoAdj + -1.0*corr*sig1*sig2*(U-lastU)/365.0;
%                 lastU = U;
%              end
%              
%              expQuantoAdj = exp(quantoAdj);
%              out.value = fwd_NM * expQuantoAdj;
%              out.quantoAdjFactor = expQuantoAdj;
             
        end
        
        function out = CommoFwdNMMCReduced(eqCOMDupireSpotGF,observeTime,futuresStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             stochasticFwd = futuresStates(:,idxNM);
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCReducedNMonths(eqCOMDupireSpotGF,observeTime,futuresStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
            forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFuturesNMonths');
            
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             stochasticFwd = futuresStates(:,idxNM);
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCReducedSimpleQuantoAdj(eqCOMDupireSpotGF,observeTime,futuresStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             stochasticFwd = futuresStates(:,idxNM);
             expQuantoAdj = eqCOMDupireSpotGF.DetATMQuantoAdj(observeTime);
             
             out = stochasticFwd * expQuantoAdj;
        end
        
        function out = CommoFwdContractMMCReduced(eqCOMDupireSpotGF,observeTime,tenorMaturityTime,futuresStates)
            forwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(tenorMaturityTime == forwardMaturity);
             if isempty(idx)
                 error('contractM is not in the reducedFutures!!')
%                 idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             stochasticFwd = futuresStates(:,idxNM);
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCInterp(eqCOMDupireSpotGF,observeTime,futuresStates)
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             % interpol using reducedFutures
             targetExpiry = forwardCurve(idxNM,1);
             
             reducedFutures = eqCOMDupireSpotGF.modelParams('reducedFutures');
             reducedFuturesDays = reducedFutures(:,1)';
             futuresStateSize = size(futuresStates,1);
             stochasticFwd = zeros(futuresStateSize,1);
             for i=1:futuresStateSize
                 stochasticFwd(i) = H_interpolation(reducedFuturesDays,futuresStates(i,:),targetExpiry,1);
             end
             %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
%              stateSize = length(modelStates);
%              stateSize = size(modelStates,2);
             
%              stochasticFwd = zeros(stateSize,1);
             
%              stochasticFwd = futuresStates(:,idxNM);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = futuresStates(idxNM,i); 
%              end
             
             out = stochasticFwd;
        end
        
        function out = initFuturesStates(eqCOMDupireSpotGF,NMC)
            reducedForwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
           reducedForwardCurveSize = size(reducedForwardCurve,1);
           reducedForwardMaturity = reducedForwardCurve(:,1); 
           
           initFuturesStatesDefault = zeros(reducedForwardCurveSize,NMC);
           
           for idx=1:reducedForwardCurveSize
                initFuturesStatesDefault(idx,:) = reducedForwardCurve(idx,2)*ones(1,NMC);
           end
           
           % we choose transpose for convenience
           initFuturesStates = initFuturesStatesDefault';
           
           nextFuturesStates = initFuturesStates;
           
           out = nextFuturesStates;
        end
        
        function out = computeStepdown1SMCEQ(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            numOfFactors = 2;
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 

                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
%            % initial modelState
%            initX = ones(NMC,1);
           
           % initial model States (futuresState)
           forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           forwardCurveSize = size(forwardCurve,1);
           forwardMaturity = forwardCurve(:,1); 
%            idx = find(0.0 <= forwardMaturity);
%            if isempty(idx)
% %               idxNM = forwardCurveSize;
%                 error('no alive futures!')
%            else
%               idxNM = min(idx);
%            end
           
           initFuturesStatesDefault = zeros(forwardCurveSize,NMC);
           
           for idx=1:forwardCurveSize
                initFuturesStatesDefault(idx,:) = forwardCurve(idx,2)*ones(1,NMC);
           end
           
           % we choose transpose for convenience
           initFuturesStates = initFuturesStatesDefault';
           
           nextFuturesStates = initFuturesStates;
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
%            nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextFuturesStates);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextFuturesStates,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    
                    nextFuturesStates = mcmcOut.nextFuturesStates;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextFuturesStates);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCAutocallAdded(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            numOfFactors = 2;
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 

                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
%            % initial modelState
%            initX = ones(NMC,1);
           
         %% initial model States (reducedFuturesState + autoCallObserve)
           
           reducedForwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
           reducedForwardCurveSize = size(reducedForwardCurve,1);
           reducedForwardMaturity = reducedForwardCurve(:,1); 
           
           aliveAutocallDays = autoCallSchedule.days(lastAliveExeriseIdx:end);
           
           newReducedForwardMaturity = sort(union(reducedForwardMaturity,aliveAutocallDays),'ascend');
           
           forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           forwardCurveSize = size(forwardCurve,1);
           forwardMaturity = forwardCurve(:,1); 
           
           reducedForwardCurve2 = [];
           for idx11=1:length(newReducedForwardMaturity)
             idx = find(newReducedForwardMaturity(idx11) <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             reducedForwardCurve2=[reducedForwardCurve2;forwardCurve(idxNM,:)];
             
           end
           
           reducedForwardCurveSize2 = size(reducedForwardCurve2,1);
           initFuturesStatesDefault = zeros(reducedForwardCurveSize2,NMC);
           
           for idx=1:reducedForwardCurveSize2
                initFuturesStatesDefault(idx,:) = reducedForwardCurve2(idx,2)*ones(1,NMC);
           end
           
           % we choose transpose for convenience
           initFuturesStates = initFuturesStatesDefault';
           
           nextFuturesStates = initFuturesStates;
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
%            nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCInterp(currentTime,nextFuturesStates);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewInterp(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextFuturesStates,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    
                    nextFuturesStates = mcmcOut.nextFuturesStates;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCInterp(currentTime,nextFuturesStates);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCInterp(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            numOfFactors = 2;
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 

                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
%            % initial modelState
%            initX = ones(NMC,1);
           
         %% initial model States (reducedFuturesState)
           
           reducedForwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
           reducedForwardCurveSize = size(reducedForwardCurve,1);
           reducedForwardMaturity = reducedForwardCurve(:,1); 
           
           initFuturesStatesDefault = zeros(reducedForwardCurveSize,NMC);
           
           for idx=1:reducedForwardCurveSize
                initFuturesStatesDefault(idx,:) = reducedForwardCurve(idx,2)*ones(1,NMC);
           end
           
           % we choose transpose for convenience
           initFuturesStates = initFuturesStatesDefault';
           
           nextFuturesStates = initFuturesStates;
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
%            nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCInterp(currentTime,nextFuturesStates);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewInterp(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextFuturesStates,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    
                    nextFuturesStates = mcmcOut.nextFuturesStates;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCInterp(currentTime,nextFuturesStates);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCReduced(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            numOfFactors = 2;
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 

                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
%            % initial modelState
%            initX = ones(NMC,1);
           
         %% initial model States (reducedFuturesState)
           nextFuturesStates = eqCOMDupireSpotGF.initFuturesStates(NMC);
           
           realizedCorr = zeros(MCTimeStep,10);
           realizedTimeStep = zeros(MCTimeStep,1);
%            reducedForwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
%            reducedForwardCurveSize = size(reducedForwardCurve,1);
%            reducedForwardMaturity = reducedForwardCurve(:,1); 
%            
%            initFuturesStatesDefault = zeros(reducedForwardCurveSize,NMC);
%            
%            for idx=1:reducedForwardCurveSize
%                 initFuturesStatesDefault(idx,:) = reducedForwardCurve(idx,2)*ones(1,NMC);
%            end
%            
%            % we choose transpose for convenience
%            initFuturesStates = initFuturesStatesDefault';
%            
%            nextFuturesStates = initFuturesStates;


%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
%            nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCReduced(currentTime,nextFuturesStates);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewReducedQuanto(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextFuturesStates,U(:,2*(idx-1)+1:2*(idx-1)+numOfFactors));
                    
                    nextFuturesStates = mcmcOut.nextFuturesStates;
                    
                    if strcmp(eqCOMDupireSpotGF.modelParams('computeRealizedCorrelationYN'),'true')
                        realizedCorr(idx,1) = mcmcOut.corrInfo.inCurveCorrB(1,2);
                        
                        realizedTimeStep(idx) = timeStep(idx+1);
                    end

%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCReduced(currentTime,nextFuturesStates);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCReduced_Square(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            numOfFactors = 2;
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 

                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
%            % initial modelState
%            initX = ones(NMC,1);
           
         %% initial model States (reducedFuturesState)
           nextFuturesStates = eqCOMDupireSpotGF.initFuturesStates(NMC);
           
           realizedCorr = zeros(MCTimeStep,10);
           realizedTimeStep = zeros(MCTimeStep,1);
%            reducedForwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
%            reducedForwardCurveSize = size(reducedForwardCurve,1);
%            reducedForwardMaturity = reducedForwardCurve(:,1); 
%            
%            initFuturesStatesDefault = zeros(reducedForwardCurveSize,NMC);
%            
%            for idx=1:reducedForwardCurveSize
%                 initFuturesStatesDefault(idx,:) = reducedForwardCurve(idx,2)*ones(1,NMC);
%            end
%            
%            % we choose transpose for convenience
%            initFuturesStates = initFuturesStatesDefault';
%            
%            nextFuturesStates = initFuturesStates;


%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
%            nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCReduced(currentTime,nextFuturesStates);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewReducedQuanto_Square(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextFuturesStates,U(:,2*(idx-1)+1:2*(idx-1)+numOfFactors));
                    
                    nextFuturesStates = mcmcOut.nextFuturesStates;
                    
                    if strcmp(eqCOMDupireSpotGF.modelParams('computeRealizedCorrelationYN'),'true')
                        realizedCorr(idx,1) = mcmcOut.corrInfo.inCurveCorrB(1,2);
                        
                        realizedTimeStep(idx) = timeStep(idx+1);
                    end

%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCReduced(currentTime,nextFuturesStates);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCReducedSimpleQuantoAdj(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            numOfFactors = 2;
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 

                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
%            % initial modelState
%            initX = ones(NMC,1);
           
         %% initial model States (reducedFuturesState)
           nextFuturesStates = eqCOMDupireSpotGF.initFuturesStates(NMC);
           
           realizedCorr = zeros(MCTimeStep,10);
           realizedTimeStep = zeros(MCTimeStep,1);
%            reducedForwardCurve = eqCOMDupireSpotGF.modelParams('reducedFutures');
%            reducedForwardCurveSize = size(reducedForwardCurve,1);
%            reducedForwardMaturity = reducedForwardCurve(:,1); 
%            
%            initFuturesStatesDefault = zeros(reducedForwardCurveSize,NMC);
%            
%            for idx=1:reducedForwardCurveSize
%                 initFuturesStatesDefault(idx,:) = reducedForwardCurve(idx,2)*ones(1,NMC);
%            end
%            
%            % we choose transpose for convenience
%            initFuturesStates = initFuturesStatesDefault';
%            
%            nextFuturesStates = initFuturesStates;


%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
%            nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCReducedSimpleQuantoAdj(currentTime,nextFuturesStates);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNewReducedQuanto(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextFuturesStates,U(:,2*(idx-1)+1:2*(idx-1)+numOfFactors));
                    mcmcOut   = inductMCForwardNewReduced(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextFuturesStates,U(:,2*(idx-1)+1:2*(idx-1)+numOfFactors));
                    
                    nextFuturesStates = mcmcOut.nextFuturesStates;
                    
                    if strcmp(eqCOMDupireSpotGF.modelParams('computeRealizedCorrelationYN'),'true')
                        realizedCorr(idx,1) = mcmcOut.corrInfo.inCurveCorrB(1,2);
                        
                        realizedTimeStep(idx) = timeStep(idx+1);
                    end

%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCReducedSimpleQuantoAdj(currentTime,nextFuturesStates);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            eqCOMDupireSpotGF.localVolSurface.volProxy = ones(size(fwdMoneyness))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 40000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = unhitValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

%         function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             %% generate local vol pricing grid start
%             basePrice = stepdownParams.params('basePrice');
%             eqCOMDupireSpotGF.basePrice = basePrice;
%             
%             volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
%             fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
%             impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
%             expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
%             fwdNM = zeros(size(expiry));
%             for i=1:length(fwdNM)
%                 fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
%             end
%             
%             % grid size is log equi distant with 0.5% size
%             dy = 0.0025;
%               
%             X_max = 2.5;
%             X_min = 0.1;
%             
%             K = round((X_max-X_min)/dy);
%             temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
%             temp_pricingVolGrid = zeros(size(volProxy,1),K+1);
% 
%             pricingVolGridSize = K+1;
%             
%             for i=1:size(volProxy,1)
%                 fwdMoneynessPerExpiry = fwdMoneyness(i,:);
%                 volProxyPerExpiry = volProxy(i,:);
%                 
%                 for j=1:K+1
%                       temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
%                       temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
%                 end
%             end
%             
%             volNodeFwdCurve = zeros(length(expiry),2);
%             
%             for i=1:length(expiry)
%                 volNodeFwdCurve(i,1) = expiry(i);
%                 volNodeFwdCurve(i,2) = fwdNM(i);
%             end
%             
%             pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
%             pricingReducedForwardGrid = pricingForwardGrid;
%             pricingVolGrid = temp_pricingVolGrid;
%                 
%             eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
%             eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
%             eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
%             eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
%             
%             %% pricing PDE Grid
%             
%             modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
%             modelStates = modelStatesFixedGrid;
%             eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
%             modelStatesSize = length(modelStatesFixedGrid);
%           
%             %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
%             
%             
%           %% PricingIdx & WeightNextPriceIndex update start
%            
%            spotLevel = 1.0;
%            
%            isFoundSpotLevel = 'false'; 
%            for i=1:modelStatesSize-1
%                
%                if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
%                    PricingIdx = i;
%                    WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
%                    isFoundSpotLevel = 'true';
%                    break;
%                end
%            end
%            
%            if strcmp(isFoundSpotLevel,'false')
%                error('spot price is out of grid range!');
%            end
%            
%           %% PricingIdx & WeightNextPriceIndex update end
%             
%             % model schedule generation
%             scheduleInt = stepdownParams.params('autoCallScheduleInt');
%             scheduleSize = size(scheduleInt,1);
%             autoCallSchedule=[];
%             for i=1:scheduleSize
%                 autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
%                 autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
%                 autoCallSchedule.strike(i) = scheduleInt(i,2);
%                 autoCallSchedule.coupon(i) = scheduleInt(i,3);
%             end
%             
%             expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
%             
%             % if valueDate is passed expiryDate then price is 0
%             maturity = DateDiff(expiryDate,valueDate);
%             if maturity <=0
%                 out = 0;
%                 return;
%             end
%             
%             expiredChance = 0;
%             aliveChance = 0;
%             expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
%             volExpiry = expiry(find(expiry <= maturity));
%             % we include valueDate in the scheduel
%             volExpiry =[volExpiry;0];
%             
%             timeStep = volExpiry;
%             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
%                 dailyTimeSteps = [maturity:-1:0]';
%                 timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
%                 
%             end
%             % we include exerciseDates
%             for i= 1:scheduleSize
%                 daysToExercise = autoCallSchedule.days(i);
%                 if daysToExercise <= 0
%                     expiredChance = expiredChance +1;
%                     continue;
%                 else
%                     aliveChance = aliveChance + 1;
%                     timeStep = [timeStep; daysToExercise];
%                 end 
%             end
%             lastAliveExeriseIdx = 1 + expiredChance;
%             
%             
%             timeStep = sort(union(timeStep,maturity),'ascend');
%             totalTimeStepSize = length(timeStep);
%             eventTimeIdx = zeros(scheduleSize,1);
%             
%             for i= scheduleSize:-1:lastAliveExeriseIdx
%                 idx = find(timeStep == autoCallSchedule.days(i));
%                 eventTimeIdx(i) = min(idx);
%             end
%            
%           %% grid generation based on basePrice
%             
%            
%           %% payoff at maturity
%            nominal = stepdownParams.params('nominal');
%            basePrice = stepdownParams.params('basePrice');
%            lowerBarrier = stepdownParams.params('lowerBarrier');
%            overHedgeShift = stepdownParams.params('overHedgeShift');
%            overHedgeSpread = stepdownParams.params('overHedgeSpread');
%            
%            callStrike1 = stepdownParams.params('callStrike1');
%            callValue1 = stepdownParams.params('callValue1');
%            SSpayoffYN = stepdownParams.params('SSpayoffYN');
%            
%            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
%            
%            modelStatesSize = length(modelStates);
%            
%            %down barrier touch
%            hitValue.npv = 0;
%            hitValue.payoff = zeros(modelStatesSize,1);
%            hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
%            hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
%            
%            % down barrier no touch
%            unhitValue.npv = 0;
%            unhitValue.payoff = zeros(modelStatesSize,1);
%            unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
%            unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
%            
%            % dummy nearest month future price
%            nMFuture.npv = 0;
%            nMFuture.payoff = zeros(modelStatesSize,1);
%            nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
%            nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
%            
%            % intermediate variables
%            payoffStateA.cashflow = zeros(modelStatesSize,1);
%            payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
%            
%            payoffStateB.cashflow = zeros(modelStatesSize,1);
%            payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%            
%            payoffStateC.cashflow = zeros(modelStatesSize,1);
%            payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
%            
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
%           
%           %% fixedGrid fwd
% %            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
%            
%            strikeMat = autoCallSchedule.strike(scheduleSize);
%            couponMat = autoCallSchedule.coupon(scheduleSize);
%            
% %            strikeOH = strikeMat + overHedgeShift;
%            % samsung overhedge payoff
%            if strcmp(SSpayoffYN,'YES')
%                for i=1:modelStatesSize
%                    if comFwd(i) < basePrice*callStrike1
%                         payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
%                    elseif comFwd(i) < basePrice*strikeMat 
%                        payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
%                    else
%                        payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
%                    end
%                end
% 
%                payoffStateB.cashflow = payoffStateA.cashflow;
% 
%                for i=1:modelStatesSize
%                     if comFwd(i) > basePrice*lowerBarrier
%                         payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
%                     end
%                end
%                
%            else
%                for i=1:modelStatesSize
%                    if comFwd(i) >= basePrice*strikeMat
%                        payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
%                    else
%                        payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
%                        payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
%                    end
%                end
% 
%                payoffStateB.cashflow = payoffStateA.cashflow;
% 
%                for i=1:modelStatesSize
%                     if comFwd(i) > basePrice*lowerBarrier
%                         payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
%                     end
%                end
%            end
%            
%            payoffStateC.cashflow = comFwd;
%            
%            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%            
%            % we don't discount forward price
%            for i=1:modelStatesSize
%                 payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
%                 payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
%                 payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
%            end
%            
%            
%            %process payoff at maturity
%             hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
%             hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
%             hitValue.payoff = payoffStateA.cashflow_npv;
%             
%             unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
%             unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
%             unhitValue.payoff = payoffStateB.cashflow_npv;
%             
%             nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
%             nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
%             nMFuture.payoff = payoffStateC.cashflow_npv;
%             
%            lastTimeIdx = currentTimeIdx;
%            
%            
%            for i=scheduleSize:-1:lastAliveExeriseIdx
%                 % past schedule neglect
%                 if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
%                 if i > lastAliveExeriseIdx
%                     startTimeIdx = eventTimeIdx(i);
%                     endTimeIdx = eventTimeIdx(i-1);
%                 else
%                     startTimeIdx = eventTimeIdx(i);
%                     endTimeIdx = 1;  % valueDate
%                 end
%                 
%                 endTimeIdx = endTimeIdx + 1;
%             %% induction start
%                 mesh = hitValue.payoff;
%                 meshB = unhitValue.payoff;
%                 for idx= startTimeIdx:-1:endTimeIdx
% %                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
% %                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
% %                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
% %                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
%                     
% %                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
% %                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     
%                     mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     % one step backward induction end
%                     % barrier check
%                     lastTimeIdx = lastTimeIdx -1;
%                     currentTime = timeStep(lastTimeIdx);
%                     
%                   %% fixedGrid fwd
% %                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
%                    
%                     for j=1:modelStatesSize
%                         if comFwd(j) <= basePrice*lowerBarrier
%                            meshB(j) = mesh(j); 
%                         end
%                     end
%                 end
%                 
%                 hitValue.payoff = mesh;
%                 unhitValue.payoff = meshB;
%                 nMFuture.payoff = comFwd;
%               %% induction end
%                 
%                 % backward induction in the payoff script
%                 currentNodeIdx = currentNodeIdx -1;
%               %% AtDate operation on Early ExerciseDate
%                 
%                 if i > lastAliveExeriseIdx
%                     currentTime = timeStep(lastTimeIdx);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValue  = hitValue.payoff/onePayoffD;
%                     contiValueB = unhitValue.payoff/onePayoffD;
%                     
%                     %AutoCall applied
%                  %% fixedGrid fwd
% %                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
%                     strikeEarly = autoCallSchedule.strike(i-1);
%                     couponEarly = autoCallSchedule.coupon(i-1);
%                     
%                      % intermediate variables
%                     payoffStateA.cashflow = zeros(modelStatesSize,1);
%                     payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     
%                     payoffStateC.cashflow = zeros(modelStatesSize,1);
%                     payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
%                     
%                     % samsung overhedge payoff
%                     if strcmp(SSpayoffYN,'YES')
%                         for j=1:modelStatesSize
%                             if comFwd(j)/basePrice >= strikeEarly
%                                payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
%                                payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
%                             elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
%                                payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                
%                                payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                             else
% %                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% %                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% % 
% %                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
% %                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
%                                 
%                                 payoffStateA.cashflow(j) = contiValue(j);
%                                 payoffStateB.cashflow(j) = contiValueB(j);
%                            end
%                         end
%                     else
%                         for j=1:modelStatesSize
%                             if comFwd(j) >= basePrice*strikeEarly
%                                payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
%                                payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
%                             else
%                                payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
%                            end
%                         end
%                         
%                     end
%                     % barrier
%                     for j=1:modelStatesSize
%                         if comFwd(j) <= basePrice*lowerBarrier
%                            payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
%                         end
%                     end
%                     
%                     payoffStateC.cashflow = comFwd;
%                     
%                     for j=1:modelStatesSize
%                         payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
%                         payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
%                         payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
%                     end
%                     
%                     %process payoff at early exercise date
%                     hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
%                     hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
%                     hitValue.payoff = payoffStateA.cashflow_npv;
%                     
%                     unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
%                     unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
%                     unhitValue.payoff = payoffStateB.cashflow_npv;
%                     
%                     nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
%                     nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
%                     nMFuture.payoff = payoffStateC.cashflow_npv;
%                     
%                 end
%                    
%            end
%            
%            
%             %% interpolate on the grid
%             hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
%                                  + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
%                              
%             unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
%                                  + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
%                              
%             nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
%                                  + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
%             
%            
%            out.hitValue = hitValue; 
%            out.unhitValue = unhitValue;
%            out.nMFuture = nMFuture; 
%         end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           dummyMeshB = zeros(length(timeStep),2);
           dummyIdx = 1;
           dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
           dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
           dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                    %apply american option
                    comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValueB  = meshB/onePayoffD;
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    if strcmp(vanillaParams.params('callPutFlag'),'C')
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
                            if payoffStateB.cashflow(j) > contiValueB(j)
                                ccc = 1.0;
                            end
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                        
                    else
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                    end
                    payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
                    meshB = payoffStateB.cashflow_npv;
                    dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
                    dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
                    dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = europeanValue.payoff(Pricingidx);
           americanValue.npv = americanValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');    
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            numOfFactors = 2;
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
%            % initial modelState
%            initX = ones(NMC,1);
%            
           % initial model States (futuresState)
           forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           forwardCurveSize = size(forwardCurve,1);
           forwardMaturity = forwardCurve(:,1); 
%            idx = find(0.0 <= forwardMaturity);
%            if isempty(idx)
% %               idxNM = forwardCurveSize;
%                 error('no alive futures!')
%            else
%               idxNM = min(idx);
%            end
           
           initFuturesStatesDefault = zeros(forwardCurveSize,NMC);
           
           for idx=1:forwardCurveSize
                initFuturesStatesDefault(idx,:) = forwardCurve(idx,2)*ones(1,NMC);
           end
           
           % we choose transpose for convenience
           initFuturesStates = initFuturesStatesDefault';
           nextFuturesStates = initFuturesStates;
           
%            nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextFuturesStates,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    
                    nextFuturesStates = mcmcOut.nextFuturesStates;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextFuturesStates);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            europeanValue.payoffUnd = payoffStateA.cashflow;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           europeanValue.npvUnd = mean(europeanValue.payoffUnd);
           
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeCalendarSpreadOptionMCReduced(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');    
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            numOfFactors = 2;
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
%            % initial modelState
%            initX = ones(NMC,1);
%            
           % initial model States (futuresState)
            nextFuturesStates = eqCOMDupireSpotGF.initFuturesStates(NMC);
            
%            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%            forwardCurveSize = size(forwardCurve,1);
%            forwardMaturity = forwardCurve(:,1); 
% %            idx = find(0.0 <= forwardMaturity);
% %            if isempty(idx)
% % %               idxNM = forwardCurveSize;
% %                 error('no alive futures!')
% %            else
% %               idxNM = min(idx);
% %            end
%            
%            initFuturesStatesDefault = zeros(forwardCurveSize,NMC);
%            
%            for idx=1:forwardCurveSize
%                 initFuturesStatesDefault(idx,:) = forwardCurve(idx,2)*ones(1,NMC);
%            end
%            
%            % we choose transpose for convenience
%            initFuturesStates = initFuturesStatesDefault';
%            nextFuturesStates = initFuturesStates;
           
%            nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    mcmcOut   = inductMCForwardNewReduced(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextFuturesStates,U(:,2*(idx-1)+1:2*(idx-1)+numOfFactors));
                    
                    nextFuturesStates = mcmcOut.nextFuturesStates;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           longTenorMaturityDate = H_Date(vanillaParams.params('longTenorMaturityDate'));
           shortTenorMaturityDate = H_Date(vanillaParams.params('shortTenorMaturityDate'));
           
           longTenorMaturityTime = DateDiff(longTenorMaturityDate,valueDate);
           shortTenorMaturityTime = DateDiff(shortTenorMaturityDate,valueDate);
           
           comFwdL = eqCOMDupireSpotGF.CommoFwdContractMMCReduced(currentTime,longTenorMaturityTime,nextFuturesStates);
           comFwdS = eqCOMDupireSpotGF.CommoFwdContractMMCReduced(currentTime,shortTenorMaturityTime,nextFuturesStates);
           
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwdL(i) - comFwdS(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwdL(i) - comFwdS(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwdL(i) + comFwdS(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwdL(i) + comFwdS(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwdL;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            europeanValue.payoffUnd = payoffStateA.cashflow;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           europeanValue.npvUnd = mean(europeanValue.payoffUnd);
           
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeBarrierMCEQ(eqCOMDupireSpotGF,valueDate,barrierParams)
            % model schedule generation
            expiryDate = H_Date(barrierParams.endDate);
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(barrierParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = barrierParams.params('nominal');
           basePrice = barrierParams.params('basePrice');
           strike =  barrierParams.params('strike');
           lowerBarrier = barrierParams.params('lowerBarrier');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.strike = strike;
           
           KIYN = barrierParams.params('KIYN');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
            % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
            comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
           isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           
           if strcmp(barrierParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                   if isKI(i)
                    payoffStateA.cashflow(i) = nominal*max(comFwd(i)/basePrice - strike,0);
                    payoffStateB.cashflow(i) = nominal*max(comFwd(i)/basePrice - strike,0);
                   end
               end
           else
               for i=1:modelStatesSize
                   if isKI(i)
                    payoffStateA.cashflow(i) = nominal*max(-comFwd(i)/basePrice + strike,0);
                    payoffStateB.cashflow(i) = nominal*max(-comFwd(i)/basePrice + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            
%             initX = ones(NMC,1);
            initX = zeros(NMC,1);
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                nextX = eqCOMDupireSpotGF.inductMCForward(timeStep(i-1),timeStep(i),startIdx,endIdx,timeScheduleInfo,nextX,dZStep,params);
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 0)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCPerExpiryTest(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            
%             initX = ones(NMC,1);
            initX = zeros(NMC,1);
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                nextX = eqCOMDupireSpotGF.inductMCForwardTest(timeStep(i-1),timeStep(i),startIdx,endIdx,timeScheduleInfo,nextX,dZStep,params);
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 0)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            initX = ones(NMC,1);
            initXIdx = ones(NMC,1)*params.Pricingidx;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            nextXIdx = initXIdx;
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextX,nextXIdx,U(:,i-1),Ks);
                nextX = mcmcOut.nextX;
                nextXIdx = mcmcOut.nextXIdx;
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
            newTimeSchedule = sort(union(volExpiry,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            if 0
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
    %             Ps = sobolset(length(dTSchedule));

                Ps = sobolset(length(dTSchedule),'Skip',NMC);
    %             Ps = scramble(Ps,'MatousekAffineOwen');
                Q = qrandstream(Ps);
                Q.reset;
                U = qrand(Q,NMC);
                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                    end
                end

               % apply brownian bridge
               dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);

               % first dZ is dummy , 0
               dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
               dZ(:,2) = dZ1(:,1);
               for i=3:size(dZ1,2)+1
                    dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
               end
           
            else
                
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = length(dTSchedule) + 1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                dZ = U;
            end
           
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardMCOTMTotalTest(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
            newTimeSchedule = sort(union(volExpiry,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            if 0
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
    %             Ps = sobolset(length(dTSchedule));

                Ps = sobolset(length(dTSchedule),'Skip',NMC);
    %             Ps = scramble(Ps,'MatousekAffineOwen');
                Q = qrandstream(Ps);
                Q.reset;
                U = qrand(Q,NMC);
                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                    end
                end

               % apply brownian bridge
               dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);

               % first dZ is dummy , 0
               dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
               dZ(:,2) = dZ1(:,1);
               for i=3:size(dZ1,2)+1
                    dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
               end
           
            else
                
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = length(dTSchedule) + 1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                dZ = U;
            end
           
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiryTest(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
            MCTimeStep = length(expiry); % -1 because 0

            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpirySimple(eqCOMDupireSpotGF,maturity,strikes)
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
%             expiry = params.expiry;
            lastP = zeros(1,length(Ks));
            lastP(Pricingidx) = 1.0;
            newP = zeros(1,length(Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = Ks;
            modelXSize = length(Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dT = dTDays/365.0;

            Ks = params.Ks;
            if strcmp(eqCOMDupireSpotGF.gridType,'uniform')
                dK = params.dK;
                dK2 = dK*dK;
                for i=1:size
                    a(i) = -0.5*dT*proxy(i)*proxy(i)/dK2;
                    b(i) = 1 + dT*proxy(i)*proxy(i)/dK2;
                    b_rg(i) = dT*proxy(i)*proxy(i)/dK2;
                    c(i) = -0.5*dT*proxy(i)*proxy(i)/dK2;
                end
            else
                
                for i=2:size-1
                    dK_i = Ks(i)-Ks(i-1);
                    dK_i1 = Ks(i+1)-Ks(i);
                    
                    a(i) = -0.5*dT*proxy(i)*proxy(i)/dK_i/(dK_i + dK_i1)*2.0;
                    b(i) = 1 + 0.5*dT*proxy(i)*proxy(i)/dK_i/dK_i1*2.0;
                    b_rg(i) = 0.5*dT*proxy(i)*proxy(i)/dK_i/dK_i1*2.0;
                    c(i) = -0.5*dT*proxy(i)*proxy(i)/dK_i1/(dK_i + dK_i1)*2.0;
                end
            end
            
            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            % use Bisection for normal Vol BackOut
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = BisecNormIV('P',0.0,K,0,maturity/365.0,0.0001,1000,pValue(i),1e-10,10000);
                impVolC(i) = BisecNormIV('C',0.0,K,0,maturity/365.0,0.0001,1000,cValue(i),1e-10,10000);
                if K <= 0.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            
            
          %% Solve  Forward PDE(GF) One time
            outGF = eqCOMDupireSpotGF.Solve1DGF(tvar,mkt_dT,optParams.dK,optParams.lastProb,optParams);
            
            newProb = outGF.newProb;
            optParams.meshProb = newProb;
           %% PDE(GF) Solve End
           % find the implied vol of dupire model
           if strcmp(eqCOMDupireSpotGF.modelParams('UseLetsBeRational'),'YES')
               target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           else
               target = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           end
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           settleFuture_idxNow = eqCOMDupireSpotGF.settleFutures(idxNow);
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                

                if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabLinearMarketFwdMoneynessRightExtrapLinear')
                    for i=1:optParams.lowerIdx-1
                        out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                    end
                    
                    for i=optParams.upperIdx+1:optParams.strikeSize
                        out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx)*(settleFuture_idxNow + optParams.marketStrikes(i))/(settleFuture_idxNow + optParams.marketStrikes(optParams.upperIdx));
                    end
                    
                elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabLinearMarketFwdMoneynessExtrapLinear')
                    for i=1:optParams.lowerIdx-1
                        out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx)*(settleFuture_idxNow+optParams.marketStrikes(i))/(settleFuture_idxNow+optParams.marketStrikes(optParams.lowerIdx));
                    end
                    
                    for i=optParams.upperIdx+1:optParams.strikeSize
                        out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx)*(settleFuture_idxNow+optParams.marketStrikes(i))/(settleFuture_idxNow+optParams.marketStrikes(optParams.upperIdx));
                    end
                else
                    for i=1:optParams.lowerIdx-1
                        out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                    end
                    
                    for i=optParams.upperIdx+1:optParams.strikeSize
                        out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                    end
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,dT,lastProb,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
%             optParams.dK = params.Ks(2) - params.Ks(1);
            optParams.dK = params.dK;
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.fwdMoneyness(idxNow,i);
            end
                
%             if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
%                 % market strike points in fwd PDE grid
%                 fwdFactor = eqCOMDupireSpotGF.FwdFactor(params.expiry(idxNow));
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i)/fwdFactor;
%                 end
%             else
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i);
%                 end
%             end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (asinh(optParams.marketStrikes(i)) - asinh(optParams.Ks(1)))/optParams.dK) + 1;  % add default 1
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastProb = lastProb;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            

            lowerIdx = 1;
            upperIdx = params.strikeSize;
            
%             if idxNow <= numOfCutoffTenor
%                 lowerIdx = min(find(optParams.marketStrikes >= lowerCutoff));
%                 upperIdx = max(find(optParams.marketStrikes <= upperCutoff));
%             end

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            
            settleFuture_idxNow = eqCOMDupireSpotGF.settleFutures(idxNow);
            % RightSide Linear Extrapol
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabLinearMarketFwdMoneynessRightExtrapLinear')
                for i=1:lowerIdx-1
                    tvar(i) = tvar(lowerIdx);
                end
                
                for i=upperIdx+1:params.strikeSize
                    tvar(i) = tvar(upperIdx)*(settleFuture_idxNow + optParams.marketStrikes(i))/(settleFuture_idxNow + optParams.marketStrikes(upperIdx));
                end
            % LeftRightSide Linear Extrapol   
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabLinearMarketFwdMoneynessExtrapLinear')
                
                for i=1:lowerIdx-1
                    tvar(i) = tvar(lowerIdx)*(settleFuture_idxNow + optParams.marketStrikes(i))/(settleFuture_idxNow + optParams.marketStrikes(lowerIdx));
                end
                
                for i=upperIdx+1:params.strikeSize
                    tvar(i) = tvar(upperIdx)*(settleFuture_idxNow + optParams.marketStrikes(i))/(settleFuture_idxNow + optParams.marketStrikes(upperIdx));
                end
                
            else
                
                for i=1:lowerIdx-1
                    tvar(i) = tvar(lowerIdx);
                end
                
                for i=upperIdx+1:params.strikeSize
                    tvar(i) = tvar(upperIdx);
                end
            end
            
            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
%             tol = 0.0001;
%             maxIter = 1000;
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
            out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            bootStrapOut.lastProb = out.newProb;
            bootStrapOut.condProb = out.condProb;
            
        end
        
        function out = CalibrateToVolExpirySABR(eqCOMDupireSpotGF,idxNow,params,calibrationFlag)
            
            %initialize calibration parameters
            calibrationType = calibrationFlag;
            
            optParams.idxNow = idxNow;
            optParams.params = params;
            optParams.strikeSize = params.strikeSize;
            optParams.marketStrikes = zeros(params.strikeSize,1);
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.fwdMoneyness(idxNow,i);
            end
            
            
            optParams.modelParamsSize = 3;  % alpha, , rho, nu
            optParams.numOfEquation = params.strikeSize + ...  % target opm options
                                      0;   % constraint

            tvar = zeros(optParams.modelParamsSize,1);
            
            initialSABRParams = params.initialSABRParams;
            
            tvar(1) = initialSABRParams(1);
            tvar(2) = initialSABRParams(2);
            tvar(3) = initialSABRParams(3);
            
            % initial parameters costval
            options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
            %                     options=[1E-03, 1E-25, 1E-25, 1E-25, 1E-25];
            x=  zeros(optParams.numOfEquation,1);
%             lb = [0.0001,-0.9999, 0.0001];
%             ub = [100.0,0.9999,100.0];
            lb = params.lb;
            ub = params.ub;
            
            tic
            
            if strcmp(calibrationFlag,'bootstrapReducedNormal3bc')
                [ret, popt, info, covar]=levmar('TargetFunctionNormalSABRReducedNormal3',tvar,x, params.maxIter, options,'bc',eqCOMDupireSpotGF,optParams);
            elseif strcmp(calibrationFlag,'bootstrapReducedLN3bc')
                [ret, popt, info, covar]=levmar('TargetFunctionLNSABRReducedLN3',tvar,x, params.maxIter, options,'bc',eqCOMDupireSpotGF,optParams);
            else
                [ret, popt, info, covar]=levmar('TargetFunctionNormalSABRReducedNormal3',tvar,x, params.maxIter, options,'unc',eqCOMDupireSpotGF,optParams);
            end
            if ret == -1
                error('unimplemnted');

            end

            toc


            out.alpha = popt(1);
            out.rho = popt(2);
            out.nu = popt(3);
            out.nIter = ret;

            out.paramsOut = zeros(3,1);
            out.paramsOut(1) = out.alpha;
            out.paramsOut(2) = out.rho;
            out.paramsOut(3) = out.nu;

            params.calibrationErrorType = 'impVolError';

            if strcmp(calibrationFlag,'bootstrapReducedNormal3bc')
                for j=1:params.strikeSize
                    market_vol = params.blackVol(idxNow,j);
                    market_otmPrice = params.blackOTMPrices(idxNow,j);
                    marketStrike = params.fwdMoneyness(idxNow,j);
                    model_vol = SABRNormalVol(0.0,marketStrike,optParams.params.expiry(idxNow)/365.0,out.alpha,out.rho,out.nu);

                    if marketStrike <= 0.0
                        model_otmPrice = NormalVanillaFwd(optParams.params.expiry(idxNow),0.0,marketStrike,model_vol,'P');
%                             model_otmPrice = blackPrice(1.0,marketStrike,model_vol,expiry(i)/365.0,-1);
                    else
                        model_otmPrice = NormalVanillaFwd(optParams.params.expiry(idxNow),0.0,marketStrike,model_vol,'C');
%                             model_otmPrice = blackPrice(1.0,marketStrike,model_vol,expiry(i)/365.0,1);
                    end
                    out.marketImpVol(j) = market_vol;
                    out.modelImpVol(j) = model_vol;
                    out.marketPrice(j) = market_otmPrice;
                    out.modelPrice(j) = model_otmPrice;
                    out.marketStrikes(j) = marketStrike;
                end
            else
                for j=1:params.strikeSize
                    market_vol = params.blackVol(idxNow,j);
                    market_otmPrice = params.blackOTMPrices(idxNow,j);
                    marketStrike = params.fwdMoneyness(idxNow,j);
                    model_vol = SABRVol(1.0,marketStrike,optParams.params.expiry(idxNow)/365.0,out.alpha,1.0,out.rho,out.nu);

                    if marketStrike <= 1.0
%                         model_otmPrice = NormalVanillaFwd(optParams.params.expiry(idxNow),0.0,marketStrike,model_vol,'P');
                            model_otmPrice = blackPrice(1.0,marketStrike,model_vol,optParams.params.expiry(idxNow)/365.0,-1);
                    else
%                         model_otmPrice = NormalVanillaFwd(optParams.params.expiry(idxNow),0.0,marketStrike,model_vol,'C');
                            model_otmPrice = blackPrice(1.0,marketStrike,model_vol,optParams.params.expiry(idxNow)/365.0,1);
                    end
                    out.marketImpVol(j) = market_vol;
                    out.modelImpVol(j) = model_vol;
                    out.marketPrice(j) = market_otmPrice;
                    out.modelPrice(j) = model_otmPrice;
                    out.marketStrikes(j) = marketStrike;
                end

            end
            
            
        end
        function out = CalibrateToFwdCorr(eqCOMDupireSpotGF,params,calibrationFlag)
        
            optParams.params = params;
            
            targetTenors = params.targetTenors;
            expirySize = length(targetTenors);
            
%             tvar = zeros(3,1);
            
            out.modelCorr = zeros(expirySize,expirySize);
            out.targetCorr = params.targetCorr;
            out.Diff = zeros(expirySize,expirySize);
            out.DiffTotal = 0.0;
            
            calibrationType = 'global';
              if nargin < 3
                calibrationType = 'global'; 
            else
                calibrationType = calibrationFlag;
            end
            N=0;
            switch calibrationType
                
            case 'global'
                tvar = zeros(3,1);
                tvar(1) = params.alpha;
                tvar(2) = params.beta;
                tvar(3) = params.rho;
                
                lb(1) = 0.0;
                lb(2) = 0.0;
                lb(3) = -0.999;
                
                ub(1) = 100.0;
                ub(2) = 100.0;
                ub(3) = 0.999;
                
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
                    
                numOfEquation = expirySize*(expirySize-1)/2;
                x=  zeros(numOfEquation,1);
                tic
                [ret, popt, info, covar]=levmar('TargetFunctionsFuturesCorrLevGlobal',tvar,x, 200, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
                out.alpha = popt(1);
                out.beta = popt(2);
                out.rho = popt(3);
                
                eqCOMDupireSpotGF.alpha = popt(1);
                eqCOMDupireSpotGF.beta = popt(2);
                eqCOMDupireSpotGF.rho = popt(3);
                
                
                N=0;
                for j=1:length(targetTenors)-1
                    for k=j+1:length(targetTenors)
                        out.modelCorr(j,k) = eqCOMDupireSpotGF.computeFuturesCorr(0.0,targetTenors(j),targetTenors(k));
                        out.Diff(j,k) = out.modelCorr(j,k)-out.targetCorr(j,k);
                        out.DiffTotal = out.DiffTotal + out.Diff(j,k)*out.Diff(j,k);
                        N = N+1;
                    end
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
                
            case 'globalInitialParamsConstraint'
                tvar = zeros(3,1);
                tvar(1) = params.alpha;
                tvar(2) = params.beta;
                tvar(3) = params.rho;
                
                optParams.params.alpha_i = params.alpha;
                optParams.params.beta_i = params.beta;
                optParams.params.rho_i = params.rho;
                
                lb(1) = 0.0;
                lb(2) = 0.0;
                lb(3) = -0.999;
                
                ub(1) = 100.0;
                ub(2) = 100.0;
                ub(3) = 0.999;
                
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
                    
%                 numOfEquation = expirySize*(expirySize-1)/2;
                numOfEquation = expirySize*(expirySize-1)/2 + 1 +1;
                
                x=  zeros(numOfEquation,1);
                tic
                [ret, popt, info, covar]=levmar('TargetFunctionsFuturesCorrLevGlobalConstraint',tvar,x, 200, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
                out.alpha = popt(1);
                out.beta = popt(2);
                out.rho = popt(3);
                
                eqCOMDupireSpotGF.alpha = popt(1);
                eqCOMDupireSpotGF.beta = popt(2);
                eqCOMDupireSpotGF.rho = popt(3);
                
                
                N=0;
                for j=1:length(targetTenors)-1
                    for k=j+1:length(targetTenors)
                        out.modelCorr(j,k) = eqCOMDupireSpotGF.computeFuturesCorr(0.0,targetTenors(j),targetTenors(k));
                        out.Diff(j,k) = out.modelCorr(j,k)-out.targetCorr(j,k);
                        out.DiffTotal = out.DiffTotal + out.Diff(j,k)*out.Diff(j,k);
                        N = N+1;
                    end
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
                
                    
            case 'globalFixedAlpha'
                tvar = zeros(2,1);
%                 tvar(1) = params.alpha;
                tvar(1) = params.beta;
                tvar(2) = params.rho;
                
                lb(1) = 0.0;
                lb(2) = -0.999;
                
                ub(1) = 100.0;
                ub(2) = 0.999;
                
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
                    
                numOfEquation = expirySize*(expirySize-1)/2;
                x=  zeros(numOfEquation,1);
                tic
                [ret, popt, info, covar]=levmar('TargetFunctionsFuturesCorrLevGlobalFixedAlpha',tvar,x, 200, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
%                 out.alpha = popt(1);
                out.beta = popt(1);
                out.rho = popt(2);
                
%                 eqCOMDupireSpotGF.alpha = popt(1);
                eqCOMDupireSpotGF.beta = popt(1);
                eqCOMDupireSpotGF.rho = popt(2);
                
                
                N=0;
                for j=1:length(targetTenors)-1
                    for k=j+1:length(targetTenors)
                        out.modelCorr(j,k) = eqCOMDupireSpotGF.computeFuturesCorr(0.0,targetTenors(j),targetTenors(k));
                        out.Diff(j,k) = out.modelCorr(j,k)-out.targetCorr(j,k);
                        out.DiffTotal = out.DiffTotal + out.Diff(j,k)*out.Diff(j,k);
                        N = N+1;
                    end
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
            
            case 'globalFixedBeta' 
                    tvar = zeros(2,1);
                tvar(1) = params.alpha;
%                 tvar(1) = params.beta;
                tvar(2) = params.rho;
                
                lb(1) = 0.0;
                lb(2) = -0.999;
                
                ub(1) = 100.0;
                ub(2) = 0.999;
                
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
                    
                numOfEquation = expirySize*(expirySize-1)/2;
                x=  zeros(numOfEquation,1);
                tic
                [ret, popt, info, covar]=levmar('TargetFunctionsFuturesCorrLevGlobalFixedAlpha',tvar,x, 200, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
                out.alpha = popt(1);
%                 out.beta = popt(1);
                out.rho = popt(2);
                
                eqCOMDupireSpotGF.alpha = popt(1);
%                 eqCOMDupireSpotGF.beta = popt(1);
                eqCOMDupireSpotGF.rho = popt(2);
                
                
                N=0;
                for j=1:length(targetTenors)-1
                    for k=j+1:length(targetTenors)
                        out.modelCorr(j,k) = eqCOMDupireSpotGF.computeFuturesCorr(0.0,targetTenors(j),targetTenors(k));
                        out.Diff(j,k) = out.modelCorr(j,k)-out.targetCorr(j,k);
                        out.DiffTotal = out.DiffTotal + out.Diff(j,k)*out.Diff(j,k);
                        N = N+1;
                    end
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
                
            case 'globalFixedRho' 
                    tvar = zeros(2,1);
                tvar(1) = params.alpha;
                tvar(2) = params.beta;
%                 tvar(2) = params.rho;
                
                lb(1) = 0.0;
                lb(2) = 0.0;
                
                ub(1) = 100.0;
                ub(2) = 100.0;
                
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
                    
                numOfEquation = expirySize*(expirySize-1)/2;
                x=  zeros(numOfEquation,1);
                tic
                [ret, popt, info, covar]=levmar('TargetFunctionsFuturesCorrLevGlobalFixedRho',tvar,x, 200, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
                out.alpha = popt(1);
                out.beta = popt(2);
%                 out.rho = popt(2);
                
                eqCOMDupireSpotGF.alpha = popt(1);
                eqCOMDupireSpotGF.beta = popt(2);
%                 eqCOMDupireSpotGF.rho = popt(2);
                
                
                N=0;
                for j=1:length(targetTenors)-1
                    for k=j+1:length(targetTenors)
                        out.modelCorr(j,k) = eqCOMDupireSpotGF.computeFuturesCorr(0.0,targetTenors(j),targetTenors(k));
                        out.Diff(j,k) = out.modelCorr(j,k)-out.targetCorr(j,k);
                        out.DiffTotal = out.DiffTotal + out.Diff(j,k)*out.Diff(j,k);
                        N = N+1;
                    end
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
                
            end
            
        end
        
        function out = CalibrateToATMVolStripGlobal(eqCOMDupireSpotGF,black,calibrationFlag)
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            expirySize = length(expiry);
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            targetExpiry = expiry;
            targetStrikes = ones(expirySize,1);
            outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
            
            params.atmImpVolStrip = outDummy.impVolSurface;
            
            
            % find option underlying futures expiry
            % futuresExpiry
            
            rawDataRefFutures = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            refFuturesExpiry = rawDataRefFutures(:,1);
            refExpiryH = expiry;

            futuresExpiry = zeros(length(refExpiryH),1);
            
            for idxhh=1:expirySize
                idxFutures = find(refFuturesExpiry > expiry(idxhh));
                if isempty(idxFutures)
                    error('no futures for option maturity!')
                else
                    idxFutures= min(idxFutures);
                    futuresExpiry(idxhh) = rawDataRefFutures(idxFutures,1);
                end
            end
            
            params.futuresExpiry = futuresExpiry;
            
            if length(futuresExpiry) ~= length(expiry)
                error('futuresExpiy size should match expiry size')
            end
            
            params.alpha = eqCOMDupireSpotGF.alpha;
            params.beta = eqCOMDupireSpotGF.beta;
            params.rho = eqCOMDupireSpotGF.rho;
%             params.sigma_flat = eqCOMDupireSpotGF.sigma_flat;
            params.sigma_flat = params.atmImpVolStrip(end);
            eqCOMDupireSpotGF.sigma_flat = params.sigma_flat;
            
            
            params.sigma_Short = params.atmImpVolStrip(1);
            params.sigma_Long  = params.atmImpVolStrip(end);
            
            eqCOMDupireSpotGF.sigma_Short = params.sigma_Short;
            eqCOMDupireSpotGF.sigma_Long  = params.sigma_Long;
            
            optParams.params = params;
            
            out.modelVol = zeros(expirySize,1);
            out.marketVol = params.atmImpVolStrip;
            
            out.Diff = zeros(expirySize,1);
            out.DiffTotal = 0.0;
            
            calibrationType = 'global';
            
            if nargin < 3
                calibrationType = 'global'; 
            else
                calibrationType = calibrationFlag;
            end
            N=0;
            switch calibrationType
                
            case 'global'
                tvar = zeros(4,1);
                tvar(1) = params.sigma_flat;
                tvar(1 + 1) = params.alpha;
                tvar(2 + 1) = params.beta;
                tvar(3 + 1) = params.rho;
                
                lb(1) = 0.0;
                lb(1 + 1) = 0.0;
                lb(2 + 1) = 0.0;
                lb(3 + 1) = -0.999;
                
                ub(1) = 100.0;
                ub(1 + 1) = 100.0;
                ub(2 + 1) = 100.0;
                ub(3 + 1) = 0.999;
                
%                 options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-6];    
%                 numOfEquation = expirySize;
                % 3 constraint on alpha & rho
                % alpha <=2 , rho <=0 & beta  >=0
                
                numOfEquation = expirySize + 1 +1 + 1;
                x=  zeros(numOfEquation,1);
                tic
                [ret, popt, info, covar]=levmar('TargetFunctionsATMVolStripLevGlobal',tvar,x, 1000, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
                out.sigma_flat = popt(1);
                out.alpha = popt(1 + 1);
                out.beta = popt(2 + 1);
                out.rho = popt(3 + 1);
                
                eqCOMDupireSpotGF.sigma_flat = popt(1);
                eqCOMDupireSpotGF.alpha = popt(1 + 1);
                eqCOMDupireSpotGF.beta = popt(2 + 1);
                eqCOMDupireSpotGF.rho = popt(3 + 1);
                
                
                N=0;
                for j=1:length(expiry)
                    out.modelVol(j) = eqCOMDupireSpotGF.computeSkewFlatModelVol(expiry(j),futuresExpiry(j));
                    out.Diff(j) = out.modelVol(j)-out.marketVol(j);
                    out.DiffTotal = out.DiffTotal + out.Diff(j)*out.Diff(j);
                    N = N+1;
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
                
            case 'globalLongShort'
                tvar = zeros(4,1);
                tvar(1) = params.sigma_Short;
                tvar(2) = params.sigma_Long;
                tvar(2 + 1) = params.beta;
                tvar(3 + 1) = params.rho;
                
                lb(1) = 0.01;
                lb(1 + 1) = 0.01;
                lb(2 + 1) = 0.0;
                lb(3 + 1) = -0.999;
                
                ub(1) = 100.0;
                ub(1 + 1) = 100.0;
                ub(2 + 1) = 100.0;
                ub(3 + 1) = 0.999;
                
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
%                 options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-6];    
%                 numOfEquation = expirySize;
                % 3 constraint on alpha & rho
                % alpha <=2 , rho <=0 & beta  >=0
                
                numOfEquation = expirySize + 1 +1;
                x=  zeros(numOfEquation,1);
                tic
                [ret, popt, info, covar]=levmar('TargetFunctionsATMVolStripLevGlobalLongShort',tvar,x, 1000, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
                out.sigma_Short = min(max(popt(1),lb(1)),ub(1));
                out.sigma_Long = min(max(popt(2),lb(2)),ub(2));
                out.beta = min(max(popt(3),lb(3)),ub(3));
                out.rho = popt(3 + 1);
                
                out.paramsList = zeros(4,1);
                out.paramsList(1) = out.sigma_Short;
                out.paramsList(2) = out.sigma_Long;
                out.paramsList(3) = out.beta;
                out.paramsList(4) = out.rho;
                
                eqCOMDupireSpotGF.sigma_Short = out.sigma_Short;
                eqCOMDupireSpotGF.sigma_Long  = out.sigma_Long;
                
                eqCOMDupireSpotGF.beta = popt(2 + 1);
                eqCOMDupireSpotGF.rho = popt(3 + 1);
                
                
                N=0;
                for j=1:length(expiry)
                    out.modelVol(j) = eqCOMDupireSpotGF.computeLongShortVolModelVol(expiry(j),futuresExpiry(j));
                    out.Diff(j) = out.modelVol(j)-out.marketVol(j);
                    out.DiffTotal = out.DiffTotal + out.Diff(j)*out.Diff(j);
                    N = N+1;
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
                
            case 'globalAlphaFixed'
                tvar = zeros(3,1);
                tvar(1) = params.sigma_flat;
%                 tvar(1 + 1) = params.alpha;
                tvar(1 + 1) = params.beta;
                tvar(2 + 1) = params.rho;
                
                lb(1) = 0.0;
%                 lb(1 + 1) = 0.0;
                lb(1 + 1) = 0.0;
                lb(2 + 1) = -0.999;
                
                ub(1) = 100.0;
%                 ub(1 + 1) = 100.0;
                ub(1 + 1) = 100.0;
                ub(2 + 1) = 0.999;
                
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
%                 options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-6];    
%                 numOfEquation = expirySize;
                % 3 constraint on alpha & rho
                % alpha <=2 , rho <=0 & beta  >=0
                
                numOfEquation = expirySize + 1 + 1;
                x=  zeros(numOfEquation,1);
                tic
                [ret, popt, info, covar]=levmar('TargetFunctionsATMVolStripLevGlobalAlphaFixed',tvar,x, 1000, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
                out.sigma_flat = popt(1);
%                 out.alpha = popt(1 + 1);
                out.beta = popt(1 + 1);
                out.rho = popt(2 + 1);
                
                eqCOMDupireSpotGF.sigma_flat = popt(1);
%                 eqCOMDupireSpotGF.alpha = popt(1 + 1);
                eqCOMDupireSpotGF.beta = popt(1 + 1);
                eqCOMDupireSpotGF.rho = popt(2 + 1);
                
                
                N=0;
                for j=1:length(expiry)
                    out.modelVol(j) = eqCOMDupireSpotGF.computeSkewFlatModelVol(expiry(j),futuresExpiry(j));
                    out.Diff(j) = out.modelVol(j)-out.marketVol(j);
                    out.DiffTotal = out.DiffTotal + out.Diff(j)*out.Diff(j);
                    N = N+1;
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
            case 'globalSigmaFixed'
                tvar = zeros(3,1);
                tvar(1) = params.alpha;
                tvar(2) = params.beta;
                tvar(3) = params.rho;
                
                lb(1) = 0.0;
                lb(2) = 0.0;
                lb(3) = -0.999;
                
                ub(1) = 100.0;
                ub(2) = 100.0;
                ub(3) = 0.999;
                
%                 options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-6];    
%                 numOfEquation = expirySize;
                % 3 constraint on alpha & rho
                % alpha <=2 , rho <=0 & beta  >=0
                
                numOfEquation = expirySize +1 + 1 +1;
                x=  zeros(numOfEquation,1);
                tic
                [ret, popt, info, covar]=levmar('TargetFunctionsATMVolStripLevGlobalSigmaFixed',tvar,x, 1000, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
                out.alpha = popt(1);
                out.beta = popt(2);
                out.rho = popt(3);
                
                eqCOMDupireSpotGF.alpha = popt(1);
                eqCOMDupireSpotGF.beta = popt(2);
                eqCOMDupireSpotGF.rho = popt(3);
                
                
                N=0;
                for j=1:length(expiry)
                    out.modelVol(j) = eqCOMDupireSpotGF.computeSkewFlatModelVol(expiry(j),futuresExpiry(j));
                    out.Diff(j) = out.modelVol(j)-out.marketVol(j);
                    out.DiffTotal = out.DiffTotal + out.Diff(j)*out.Diff(j);
                    N = N+1;
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
                
             case 'globalSigmaAlphaFixed'
                tvar = zeros(2,1);
                tvar(1) = params.beta;
                tvar(2) = params.rho;
                
                lb(1) = 0.0;
                lb(2) = -0.999;
                
                ub(1) = 100.0;
                ub(2) = 0.999;
                
                options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
%                 options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-6];    
%                 numOfEquation = expirySize;
                % 3 constraint on alpha & rho
                % alpha <=2 , rho <=0 & beta  >=0
                
                numOfEquation = expirySize+2;
                x=  zeros(numOfEquation,1);
                tic
%                 [ret, popt, info, covar]=levmar('TargetFunctionsATMVolStripLevGlobalSigmaAlphaFixedConstraint',tvar,x, 1000, options,'bc',lb,ub,eqCOMDupireSpotGF,optParams);
                
                [ret, popt, info, covar]=levmar('TargetFunctionsATMVolStripLevGlobalSigmaAlphaFixed',tvar,x, 1000, options,'unc',eqCOMDupireSpotGF,optParams);
                toc
                
                out.beta = popt(1);
                out.rho = popt(2);
                
                eqCOMDupireSpotGF.beta = popt(1);
                eqCOMDupireSpotGF.rho = popt(2);
                
                
                N=0;
                for j=1:length(expiry)
                    out.modelVol(j) = eqCOMDupireSpotGF.computeSkewFlatModelVol(expiry(j),futuresExpiry(j));
                    out.Diff(j) = out.modelVol(j)-out.marketVol(j);
                    out.DiffTotal = out.DiffTotal + out.Diff(j)*out.Diff(j);
                    N = N+1;
                end
                   
                out.DiffTotal = sqrt(out.DiffTotal/N);
                
            otherwise
                    disp('unImplemented')    
            end
                    
            
        
        end
        
        function out = CalibrateToVolSurfaceNormalSABR(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            

            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            if isKey(eqCOMDupireSpotGF.modelParams,'useYN')
                eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            else
                eqCOMDupireSpotGF.useYN = ones(expirySize,strikeSize);
            end
            
            if isKey(eqCOMDupireSpotGF.modelParams,'deltaCutOff')
                eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            else
                eqCOMDupireSpotGF.deltaCutOff = 0.0;
            end
            settleFuturesRef = eqCOMDupireSpotGF.settleFuturesRef;
                
            if strcmp(volSurface.params('moneyNessType'),'fixedStrike')
                
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)- fwd;
                        
                        if fwdMoneyness(k,j) <= 0.0
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
%                         blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                          blackOTMVega(k,j) = black.NormalVanillaFwdVega(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j));
                   end
                end
                
            elseif strcmp(volSurface.params('moneyNessType'),'fixedStrikeOneStep')
                settleFuturesRefSpot = eqCOMDupireSpotGF.modelParams('settleFuturesRefSpot');
%                 eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRefSpot(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            elseif strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess')
%                 settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
%                 eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = settleFuturesRef(k)*strike(j);
                        
                        if fwdMoneyness(k,j) <= 0
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'P');
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'C');
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        
                        blackOTMVega(k,j) = black.NormalVanillaFwdVega(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j));
%                         blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'normalFwdMoneyNessMatrix')
%                 settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
%                 eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                normalFwdMoneNessMatrix = eqCOMDupireSpotGF.modelParams('normalFwdMoneyNessMatrix');
                for k=1:expirySize
                    
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = normalFwdMoneNessMatrix(k,j);
                        
                        if fwdMoneyness(k,j) <= 0
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'P');
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'C');
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        
                        blackOTMVega(k,j) = black.NormalVanillaFwdVega(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j));
%                         blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'LNFwdMoneyNessMatrix')
%                 settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
%                 eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                normalFwdMoneNessMatrix = eqCOMDupireSpotGF.modelParams('LNFwdMoneyNessMatrix');
                for k=1:expirySize
                    
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = normalFwdMoneNessMatrix(k,j);
                        
                        if fwdMoneyness(k,j) <= 1.0
%                             blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
%                             blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        
%                         blackOTMVega(k,j) = black.NormalVanillaFwdVega(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j));
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR')  %% SSR
                for k=1:expirySize
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = volSurface.fwdMoneyness(k,j);
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        if strike(j) <= 0
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = norminv(-1.0*strike(j),0,1)*dummyStd;
                            
                        else
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = -1.0*norminv(strike(j),0,1)*dummyStd;
                        end

                        if fwdMoneyness(k,j) <= 0
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices2(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'P');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        else
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices2(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'C');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        end
                        blackOTMVega(k,j) = black.NormalVanillaFwdVega(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j));
                         
                    end
                    dfOut(k) = black.zeroCurve.DF(expiry(k)/365.0);
                end
                
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            if strcmp(calibrationFlag,'bootstrap3bcLNComputeTargetVol')
                params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            else
                params.Pricingidx = floor((0.0-params.Ks(1))/params.dK) + 1;
            end
            
            
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            params.initialSABRParams = eqCOMDupireSpotGF.modelParams('SABR');
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            initProb = zeros(1,params.Ns);
            initProb(params.Pricingidx) = 1.0;
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            out.marketPrices = zeros(expirySize,strikeSize);
            out.modelPrices = zeros(expirySize,strikeSize);
            
            out.lnModelVol = zeros(expirySize,strikeSize);
            out.lnMarketVol = zeros(expirySize,strikeSize);
            out.lnVolError = zeros(expirySize,strikeSize);
            
            out.alphaTerm = zeros(expirySize,1);
            out.rhoTerm = zeros(expirySize,1);
            out.nuTerm = zeros(expirySize,1);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;
            out.fwdLnVolMseTotal = 0;

            out.useYN = ones(expirySize,strikeSize);
            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap3'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
%                         bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        bootStrapOut = eqCOMDupireSpotGF.CalibrateToVolExpirySABR(i,params,'bootstrapReducedNormal3');
                        
                        % we apply floor and cap for the volProxy
                        out.alphaTerm(i) = bootStrapOut.alpha;
                        out.rhoTerm(i) = bootStrapOut.rho;
                        out.nuTerm(i) = bootStrapOut.nu;
                        
                        for j=1:strikeSize
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.volError(i,j) = out.modelImpVol(i,j) - out.marketImpVol(i,j);
                            
                            out.marketPrices(i,j) = bootStrapOut.marketPrice(j);
                            out.modelPrices(i,j) = bootStrapOut.modelPrice(j);
                            out.priceRe(i,j) = out.modelPrices(i,j)/out.marketPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            out.lnModelVol(i,j) =  LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.modelImpVol(i,j),params.expiry(i)/365.0);
                            out.lnMarketVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.marketImpVol(i,j),params.expiry(i)/365.0);
                            out.lnVolError(i,j) = out.lnModelVol(i,j) - out.lnMarketVol(i,j);
                        end
                        
                    end
                    
                    N=0;
                    out.fwdLnVolMseTotal = 0.0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if out.useYN(j,k)
                                out.rmseTotal = out.rmseTotal + out.priceRe(j,k)*out.priceRe(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                out.fwdLnVolMseTotal = out.fwdLnVolMseTotal + out.lnVolError(j,k)*out.lnVolError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    out.fwdLnVolMseTotal = sqrt(out.fwdLnVolMseTotal/N);

                case 'bootstrap3ComputeTargetVol'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
%                         bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        bootStrapOut = eqCOMDupireSpotGF.CalibrateToVolExpirySABR(i,params,'bootstrapReducedNormal3');
                        
                        % we apply floor and cap for the volProxy
                        out.alphaTerm(i) = bootStrapOut.alpha;
                        out.rhoTerm(i) = bootStrapOut.rho;
                        out.nuTerm(i) = bootStrapOut.nu;
                        
                        for j=1:strikeSize
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.volError(i,j) = out.modelImpVol(i,j) - out.marketImpVol(i,j);
                            
                            out.marketPrices(i,j) = bootStrapOut.marketPrice(j);
                            out.modelPrices(i,j) = bootStrapOut.modelPrice(j);
                            out.priceRe(i,j) = out.modelPrices(i,j)/out.marketPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            out.lnModelVol(i,j) =  LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.modelImpVol(i,j),params.expiry(i)/365.0);
                            out.lnMarketVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.marketImpVol(i,j),params.expiry(i)/365.0);
                            out.lnVolError(i,j) = out.lnModelVol(i,j) - out.lnMarketVol(i,j);
                        end
                        
                    end
                    
                    N=0;
                    out.fwdLnVolMseTotal = 0.0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if out.useYN(j,k)
                                out.rmseTotal = out.rmseTotal + out.priceRe(j,k)*out.priceRe(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                out.fwdLnVolMseTotal = out.fwdLnVolMseTotal + out.lnVolError(j,k)*out.lnVolError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    out.fwdLnVolMseTotal = sqrt(out.fwdLnVolMseTotal/N);
                    
                  %% compute implied surface for targetStrikes;
                    
                    targetExpiry = params.expiry;
                  %% targetStrike is fwdMoneyness start
                    targetStrikesReduced = 0.5:0.1:1.5;
                    for i=1:length(targetExpiry)
                        nmFwd = eqCOMDupireSpotGF.settleFuturesRef(i);
                        for j=1:size(targetStrikesReduced,2)
                            targetStrikes(i,j) = nmFwd*targetStrikesReduced(j) - nmFwd;
                        end
                    end
                    
                    eqCOMDupireSpotGF.targetStrikes = targetStrikes;
                    
                    out.targetStrikesFwd = targetStrikes;
                    out.forwardImpVolFwd = zeros(size(targetStrikes));
                    
                    for i=1:length(targetExpiry)
                        alpha1 = out.alphaTerm(i);
                        rho1 = out.rhoTerm(i);
                        nu1 = out.nuTerm(i);
                        term = targetExpiry(i)/365.0;
                        for j=1:size(targetStrikes,2)
                            out.forwardImpVolFwd(i,j) = SABRNormalVol(0.0,targetStrikes(i,j),term,alpha1,rho1,nu1);
                        end
                    end
                    
                 %% targetStrike is fwdMoneyness end
                 
                 %% targetStrike is from DeltaMoneyness start
                 
                    deltaMoneynessTarget = [-0.1	-0.2	-0.3	-0.4	-0.5	0.4	0.3	0.2	0.1];
                    out.targetStrikesDelta = zeros(length(targetExpiry),length(deltaMoneynessTarget));
                    out.forwardImpVolDelta = zeros(length(targetExpiry),length(deltaMoneynessTarget));
                    out.normalFwdDelta = zeros(length(targetExpiry),length(deltaMoneynessTarget));
                    %
                    for i=1:length(targetExpiry)
                        alpha1 = out.alphaTerm(i);
                        rho1 = out.rhoTerm(i);
                        nu1 = out.nuTerm(i);
                        term = targetExpiry(i)/365.0;
                        for j=1:size(out.targetStrikesDelta,2)
                            delta = deltaMoneynessTarget(j);
                            out.targetStrikesDelta(i,j) = TargetStrikeFromDeltaNormalSABRReduced(delta,term,alpha1,rho1,nu1);
                            out.forwardImpVolDelta(i,j) = SABRNormalVol(0.0,out.targetStrikesDelta(i,j),term,alpha1,rho1,nu1);
                            
                            if delta < 0 
                                CPFlag = 'P';
                            else
                                CPFlag = 'C';
                            end
                            
                            out.normalFwdDelta(i,j) = black.NormalVanillaFwdDelta(targetExpiry(i),0.0, ...
                                                        out.targetStrikesDelta(i,j),out.forwardImpVolDelta(i,j),CPFlag);
                        end
                    end
                    ccc = 1.0;
                %% targetStrike is from DeltaMoneyness end
                    
                case 'bootstrap3bcComputeTargetVol'
                    
                    params.lb = eqCOMDupireSpotGF.modelParams('SABR_lb');
                    params.ub = eqCOMDupireSpotGF.modelParams('SABR_ub');
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
%                         bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        bootStrapOut = eqCOMDupireSpotGF.CalibrateToVolExpirySABR(i,params,'bootstrapReducedNormal3bc');
                        
                        % we apply floor and cap for the volProxy
                        out.alphaTerm(i) = bootStrapOut.alpha;
                        out.rhoTerm(i) = bootStrapOut.rho;
                        out.nuTerm(i) = bootStrapOut.nu;
                        out.nIter(i) = bootStrapOut.nIter;
                        for j=1:strikeSize
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.volError(i,j) = out.modelImpVol(i,j) - out.marketImpVol(i,j);
                            
                            out.marketPrices(i,j) = bootStrapOut.marketPrice(j);
                            out.modelPrices(i,j) = bootStrapOut.modelPrice(j);
                            out.priceRe(i,j) = out.modelPrices(i,j)/out.marketPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            out.lnModelVol(i,j) =  LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.modelImpVol(i,j),params.expiry(i)/365.0);
                            out.lnMarketVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.marketImpVol(i,j),params.expiry(i)/365.0);
                            out.lnVolError(i,j) = out.lnModelVol(i,j) - out.lnMarketVol(i,j);
                        end
                        
                    end
                    
                    N=0;
                    out.fwdLnVolMseTotal = 0.0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if out.useYN(j,k)
                                out.rmseTotal = out.rmseTotal + out.priceRe(j,k)*out.priceRe(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                out.fwdLnVolMseTotal = out.fwdLnVolMseTotal + out.lnVolError(j,k)*out.lnVolError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    out.fwdLnVolMseTotal = sqrt(out.fwdLnVolMseTotal/N);
                    
                  %% compute implied surface for targetStrikes;
                    
                    targetExpiry = params.expiry;
                  %% targetStrike is fwdMoneyness start
                    targetStrikesReduced = 0.5:0.1:1.5;
                    for i=1:length(targetExpiry)
                        nmFwd = eqCOMDupireSpotGF.settleFuturesRef(i);
                        for j=1:size(targetStrikesReduced,2)
                            targetStrikes(i,j) = nmFwd*targetStrikesReduced(j) - nmFwd;
                        end
                    end
                    
                    eqCOMDupireSpotGF.targetStrikes = targetStrikes;
                    
                    out.targetStrikesFwd = targetStrikes;
                    out.forwardImpVolFwd = zeros(size(targetStrikes));
                    
                    for i=1:length(targetExpiry)
                        alpha1 = out.alphaTerm(i);
                        rho1 = out.rhoTerm(i);
                        nu1 = out.nuTerm(i);
                        term = targetExpiry(i)/365.0;
                        for j=1:size(targetStrikes,2)
                            out.forwardImpVolFwd(i,j) = SABRNormalVol(0.0,targetStrikes(i,j),term,alpha1,rho1,nu1);
                        end
                    end
                    
                 %% targetStrike is fwdMoneyness end
                 
                 %% targetStrike is from DeltaMoneyness start
                 
                    deltaMoneynessTarget = [-0.1	-0.2	-0.3	-0.4	-0.5	0.4	0.3	0.2	0.1];
                    out.targetStrikesDelta = zeros(length(targetExpiry),length(deltaMoneynessTarget));
                    out.forwardImpVolDelta = zeros(length(targetExpiry),length(deltaMoneynessTarget));
                    out.normalFwdDelta = zeros(length(targetExpiry),length(deltaMoneynessTarget));
                    %
                    for i=1:length(targetExpiry)
                        alpha1 = out.alphaTerm(i);
                        rho1 = out.rhoTerm(i);
                        nu1 = out.nuTerm(i);
                        term = targetExpiry(i)/365.0;
                        for j=1:size(out.targetStrikesDelta,2)
                            delta = deltaMoneynessTarget(j);
                            out.targetStrikesDelta(i,j) = TargetStrikeFromDeltaNormalSABRReduced(delta,term,alpha1,rho1,nu1);
                            out.forwardImpVolDelta(i,j) = SABRNormalVol(0.0,out.targetStrikesDelta(i,j),term,alpha1,rho1,nu1);
                            
                            if delta < 0 
                                CPFlag = 'P';
                            else
                                CPFlag = 'C';
                            end
                            
                            out.normalFwdDelta(i,j) = black.NormalVanillaFwdDelta(targetExpiry(i),0.0, ...
                                                        out.targetStrikesDelta(i,j),out.forwardImpVolDelta(i,j),CPFlag);
                        end
                    end
                    ccc = 1.0;
                %% targetStrike is from DeltaMoneyness end
                case 'bootstrap3bcLNComputeTargetVol'
                    
                    params.lb = eqCOMDupireSpotGF.modelParams('SABR_lb');
                    params.ub = eqCOMDupireSpotGF.modelParams('SABR_ub');
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
%                         bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        bootStrapOut = eqCOMDupireSpotGF.CalibrateToVolExpirySABR(i,params,'bootstrapReducedLN3bc');
                        
                        % we apply floor and cap for the volProxy
                        out.alphaTerm(i) = bootStrapOut.alpha;
                        out.rhoTerm(i) = bootStrapOut.rho;
                        out.nuTerm(i) = bootStrapOut.nu;
                        out.nIter(i) = bootStrapOut.nIter;
                        for j=1:strikeSize
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.volError(i,j) = out.modelImpVol(i,j) - out.marketImpVol(i,j);
                            
                            out.marketPrices(i,j) = bootStrapOut.marketPrice(j);
                            out.modelPrices(i,j) = bootStrapOut.modelPrice(j);
                            out.priceRe(i,j) = out.modelPrices(i,j)/out.marketPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            out.lnModelVol(i,j) =  LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.modelImpVol(i,j),params.expiry(i)/365.0);
                            out.lnMarketVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.marketImpVol(i,j),params.expiry(i)/365.0);
                            out.lnVolError(i,j) = out.lnModelVol(i,j) - out.lnMarketVol(i,j);
                        end
                        
                    end
                    
                    N=0;
                    out.fwdLnVolMseTotal = 0.0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if out.useYN(j,k)
                                out.rmseTotal = out.rmseTotal + out.priceRe(j,k)*out.priceRe(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                out.fwdLnVolMseTotal = out.fwdLnVolMseTotal + out.lnVolError(j,k)*out.lnVolError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    out.fwdLnVolMseTotal = sqrt(out.fwdLnVolMseTotal/N);
                    
                  %% compute implied surface for targetStrikes;
                    
                    targetExpiry = params.expiry;
                  %% targetStrike is fwdMoneyness start
                    targetStrikesReduced = 0.5:0.1:1.5;
                    for i=1:length(targetExpiry)
                        nmFwd = eqCOMDupireSpotGF.settleFuturesRef(i);
                        for j=1:size(targetStrikesReduced,2)
                            targetStrikes(i,j) = nmFwd*targetStrikesReduced(j);
                        end
                    end
                    
                    eqCOMDupireSpotGF.targetStrikes = targetStrikes;
                    
                    out.targetStrikesFwd = targetStrikes;
                    out.forwardImpVolFwd = zeros(size(targetStrikes));
                    
                    for i=1:length(targetExpiry)
                        alpha1 = out.alphaTerm(i);
                        rho1 = out.rhoTerm(i);
                        nu1 = out.nuTerm(i);
                        term = targetExpiry(i)/365.0;
                        for j=1:size(targetStrikes,2)
                            out.forwardImpVolFwd(i,j) = SABRVol(1.0,targetStrikes(i,j),term,alpha1,1.0,rho1,nu1);
                        end
                    end
                    
                 %% targetStrike is fwdMoneyness end
                 
%                  %% targetStrike is from DeltaMoneyness start
%                  
%                     deltaMoneynessTarget = [-0.1	-0.2	-0.3	-0.4	-0.5	0.4	0.3	0.2	0.1];
%                     out.targetStrikesDelta = zeros(length(targetExpiry),length(deltaMoneynessTarget));
%                     out.forwardImpVolDelta = zeros(length(targetExpiry),length(deltaMoneynessTarget));
%                     out.normalFwdDelta = zeros(length(targetExpiry),length(deltaMoneynessTarget));
%                     %
%                     for i=1:length(targetExpiry)
%                         alpha1 = out.alphaTerm(i);
%                         rho1 = out.rhoTerm(i);
%                         nu1 = out.nuTerm(i);
%                         term = targetExpiry(i)/365.0;
%                         for j=1:size(out.targetStrikesDelta,2)
%                             delta = deltaMoneynessTarget(j);
%                             out.targetStrikesDelta(i,j) = TargetStrikeFromDeltaNormalSABRReduced(delta,term,alpha1,rho1,nu1);
%                             out.forwardImpVolDelta(i,j) = SABRNormalVol(0.0,out.targetStrikesDelta(i,j),term,alpha1,rho1,nu1);
%                             
%                             if delta < 0 
%                                 CPFlag = 'P';
%                             else
%                                 CPFlag = 'C';
%                             end
%                             
%                             out.normalFwdDelta(i,j) = black.NormalVanillaFwdDelta(targetExpiry(i),0.0, ...
%                                                         out.targetStrikesDelta(i,j),out.forwardImpVolDelta(i,j),CPFlag);
%                         end
%                     end
                    ccc = 1.0;
                %% targetStrike is from DeltaMoneyness end
                otherwise
                disp('unImplemented')
                    
            end
        end
        
        function out = CalibrateToVolSurfaceStrikeMatrix(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
%             strikeSize = length(strike);
            strikeSize = size(strike,2);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            

            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            if isKey(eqCOMDupireSpotGF.modelParams,'useYN')
                eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            else
                eqCOMDupireSpotGF.useYN = ones(expirySize,strikeSize);
            end
            
            if isKey(eqCOMDupireSpotGF.modelParams,'deltaCutOff')
                eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            else
                eqCOMDupireSpotGF.deltaCutOff = 0.0;
            end
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrike')
                settleFuturesRef = eqCOMDupireSpotGF.settleFuturesRef;
                
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(k,j)/fwd;
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,eqCOMDupireSpotGF.fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
            
            elseif strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess')
                for k=1:expirySize
    %                 fwd = black.Fwd(spot,expiry(k));
    %                 df = black.zeroCurve.DF(expiry(k)/365.0);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(k,j);
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR')  %% SSR
                for k=1:expirySize
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = volSurface.fwdMoneyness(k,j);
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        if strike(j) <= 0
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        else
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        end

                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'P');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'C');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        end
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                         
                    end
                    dfOut(k) = black.zeroCurve.DF(expiry(k)/365.0);
                end
                
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            initProb = zeros(1,params.Ns);
            initProb(params.Pricingidx) = 1.0;
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.rmseTotal1 = 0;
            out.fwdVolMseTotal1 = 0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
%                     toc
                    
%                     tic
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    
%                     toc
                case 'bootstrapForwardSSR'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    
                    for j=1:expirySize
                        for k=1:strikeSize
                            % we report only those calibrated target only
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal1 = out.rmseTotal1 + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal1 = out.fwdVolMseTotal1 + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal1 = sqrt(out.rmseTotal1/N);
                    out.fwdVolMseTotal1 = sqrt(out.fwdVolMseTotal1/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    % compute Target implied vol
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                  %% compute implied surface for targetStrikes;
                    
                    targetExpiry = params.expiry;
                    targetStrikes = out.fwdMoneyness;
                    slope = eqCOMDupireSpotGF.slope;
                    for i=1:length(targetExpiry)
                        nmFwd = eqCOMDupireSpotGF.FwdNM(targetExpiry(i));
                        referenceNmFwd = eqCOMDupireSpotGF.ReferenceFwdNM(targetExpiry(i));
                        for j=1:size(targetStrikes,2)
                            targetStrikes(i,j) = out.fwdMoneyness(i,j)*(1.0 + slope*(nmFwd/referenceNmFwd - 1.0));
                        end
                    end
                    
                    eqCOMDupireSpotGF.targetStrikes = targetStrikes;
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    
                    targetStrikesDummy2 = [
                    0.5	0.6	0.7	0.8	0.9	1	1.1	1.2	1.3	1.4	1.5
0.5	0.6	0.7	0.8	0.9	1	1.1	1.2	1.3	1.4	1.5
0.5	0.6	0.7	0.8	0.9	1	1.1	1.2	1.3	1.4	1.5
0.5	0.6	0.7	0.8	0.9	1	1.1	1.2	1.3	1.4	1.5
0.5	0.6	0.7	0.8	0.9	1	1.1	1.2	1.3	1.4	1.5
0.5	0.6	0.7	0.8	0.9	1	1.1	1.2	1.3	1.4	1.5
                    ];
                    
                    outDummy2 = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikesDummy2);
                    
                    out.forwardImpVol = outDummy.impVolSurface;
                    out.cValueSurface = outDummy.cValueSurface;
                    out.pValueSurface = outDummy.pValueSurface;
                    out.probMeshInt = outDummy.probMeshInt;
                    
                    % construct new implied volSurface and calibrate on
                    % this surface
                    origMktData = eqCOMDupireSpotGF.mktData;
                    
                    originalVolSurfaceData = origMktData('impliedVolSurface').params('rawData');
                    
                    
                    
                    newVolSurfaceData = originalVolSurfaceData;
                    newVolSurfaceData(2:size(newVolSurfaceData,1),2:size(newVolSurfaceData,2)) = outDummy.impVolSurface(:,:);
                    
                    mktData = eqCOMDupireSpotGF.mktData('impliedVolSurface').params;
                    
                    if isKey(mktData,'parametrization')
                        mktData('parametrization') = 'nonParametric';
                    end
                    
                    mktData('rawData') = newVolSurfaceData;
                    mktData('fwdMoneyness') = out.fwdMoneyness;
                    impliedVolSurfaceMktData = MktData(mktData);
                    impliedVolSurface = EQVolSurface(impliedVolSurfaceMktData);
                    impliedVolSurface.params('moneyNessType') = 'fwdMoneyNessSSR';
                    origMktData('impliedVolSurface') = impliedVolSurface;
                    
                    newBlack =  EQBlack(EQModel(Model(origMktData,black.modelParams)));
                    
                    newOut = eqCOMDupireSpotGF.CalibrateToVolSurface(newBlack,'bootstrapForwardOnly');
%                     newOut = eqCOMDupireSpotGF.CalibrateToVolSurface(newBlack,'bootstrap');
                    
                    % 1st step calibration info
                    newOut.rmseTotal1 = out.rmseTotal1;
                    newOut.fwdVolMseTotal1 = out.fwdVolMseTotal1;
                    newOut.originalUseYN = out.useYN;
                    
                    % bumped volSurface as output
                    % originalOut 20181226
                    newOut.originalImpVolSurface = out.marketImpVol;
                    newOut.originalModelImpVol = out.modelImpVol;
                    newOut.originalVolProxy = out.volProxy;
                    newOut.originalMarketStrikes = out.marketStrikes;
                    
                    newOut.shiftedImpVolSurface = outDummy.impVolSurface;
                    newOut.targetStrikes = targetStrikes;
                    
                    out = newOut;
                    
                    
                    
                    out = newOut;
                    aaa = 1.0;
                    
                case 'bootstrapFixedStrikeOneStep'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    
                    for j=1:expirySize
                        for k=1:strikeSize
                            % we report only those calibrated target only
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal1 = out.rmseTotal1 + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal1 = out.fwdVolMseTotal1 + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal1 = sqrt(out.rmseTotal1/N);
                    out.fwdVolMseTotal1 = sqrt(out.fwdVolMseTotal1/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    % compute Target implied vol
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                  %% compute implied surface for targetStrikes;
%                     
%                     targetExpiry = params.expiry;
%                     targetStrikes = out.fwdMoneyness;
%                     slope = eqCOMDupireSpotGF.slope;
%                     for i=1:length(targetExpiry)
%                         nmFwd = eqCOMDupireSpotGF.FwdNM(targetExpiry(i));
%                         referenceNmFwd = eqCOMDupireSpotGF.ReferenceFwdNM(targetExpiry(i));
%                         for j=1:size(targetStrikes,2)
%                             targetStrikes(i,j) = out.fwdMoneyness(i,j)*(1.0 + slope*(nmFwd/referenceNmFwd - 1.0));
%                         end
%                     end
%                     
%                     eqCOMDupireSpotGF.targetStrikes = targetStrikes;
%                     
%                     outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
%                     out.forwardImpVol = outDummy.impVolSurface;
%                     out.cValueSurface = outDummy.cValueSurface;
%                     out.pValueSurface = outDummy.pValueSurface;
%                     out.probMeshInt = outDummy.probMeshInt;
%                     
%                     % construct new implied volSurface and calibrate on
%                     % this surface
%                     origMktData = eqCOMDupireSpotGF.mktData;
%                     
%                     originalVolSurfaceData = origMktData('impliedVolSurface').params('rawData');
%                     
%                     
%                     
%                     newVolSurfaceData = originalVolSurfaceData;
%                     newVolSurfaceData(2:size(newVolSurfaceData,1),2:size(newVolSurfaceData,2)) = outDummy.impVolSurface(:,:);
%                     
%                     mktData = eqCOMDupireSpotGF.mktData('impliedVolSurface').params;
%                     
%                     if isKey(mktData,'parametrization')
%                         mktData('parametrization') = 'nonParametric';
%                     end
%                     
%                     mktData('rawData') = newVolSurfaceData;
%                     mktData('fwdMoneyness') = out.fwdMoneyness;
%                     impliedVolSurfaceMktData = MktData(mktData);
%                     impliedVolSurface = EQVolSurface(impliedVolSurfaceMktData);
%                     impliedVolSurface.params('moneyNessType') = 'fwdMoneyNessSSR';
%                     origMktData('impliedVolSurface') = impliedVolSurface;
%                     
%                     newBlack =  EQBlack(EQModel(Model(origMktData,black.modelParams)));
%                     
%                     newOut = eqCOMDupireSpotGF.CalibrateToVolSurface(newBlack,'bootstrapForwardOnly');
% %                     newOut = eqCOMDupireSpotGF.SX5E(newBlack,'bootstrap');
%                     
%                     % 1st step calibration info
%                     newOut.rmseTotal1 = out.rmseTotal1;
%                     newOut.fwdVolMseTotal1 = out.fwdVolMseTotal1;
%                     newOut.originalUseYN = out.useYN;
%                     
%                     % bumped volSurface as output
%                     % originalOut 20181226
%                     newOut.originalImpVolSurface = out.marketImpVol;
%                     newOut.originalModelImpVol = out.modelImpVol;
%                     newOut.originalVolProxy = out.volProxy;
%                     newOut.originalMarketStrikes = out.marketStrikes;
%                     
%                     newOut.shiftedImpVolSurface = outDummy.impVolSurface;
%                     newOut.targetStrikes = targetStrikes;
%                     
%                     out = newOut;
%                     
%                     
%                     
%                     out = newOut;
%                     aaa = 1.0;
                case 'bootstrapForwardOnlyDebug'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    %% SSR
                    out.targetStrikes = eqCOMDupireSpotGF.targetStrikes;
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    targetExpiry = params.expiry;
                    dummyStrikes = [0.5:0.1:1.5];
                    targetStrikes = repmat(dummyStrikes,[length(targetExpiry), 1]);
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    forwardImpVolSurf = outDummy.impVolSurface;

                    targetExpiry2 = repmat(targetExpiry,[1, length(dummyStrikes)]);
                    
                    totalVar = forwardImpVolSurf.*forwardImpVolSurf.*targetExpiry2/365.0;
                    
                    diffVar = zeros(length(targetExpiry)-1,length(dummyStrikes));
                    arbitrageCheckMat = zeros((length(targetExpiry)-1)*length(dummyStrikes),1);
                    
                    for idxzz=1:length(targetExpiry)-1
                        diffVar(idxzz,:) = totalVar(idxzz+1,:)-totalVar(idxzz,:);
                    end
                    
                                        
                    arbitrageCheckSum = 0;
                    for idxzz=1:length(targetExpiry)-1
                        for idxww= 1:length(dummyStrikes)
                            if diffVar(idxzz,idxww) < 0
                                arbitrageCheckMat((idxzz-1)*(length(dummyStrikes))+ idxww,1) = 1;
                                arbitrageCheckSum = arbitrageCheckSum +1;
                            end
                            
                        end
                    end
                    
                    out.arbitrageCheckMat = arbitrageCheckMat;
                    out.arbitrageCheckSum = arbitrageCheckSum;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                  
                  
                    aaa = 1.0;
                    
                    
                      

%                     
                case 'bootstrapForwardOnly'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    %% SSR
                    out.targetStrikes = eqCOMDupireSpotGF.targetStrikes;
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                  
                  
                    aaa = 1.0;
                    
                    
                      

                otherwise
                    disp('unImplemented')
                    
            end
        end
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            

            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            if isKey(eqCOMDupireSpotGF.modelParams,'useYN')
                eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            else
                eqCOMDupireSpotGF.useYN = ones(expirySize,strikeSize);
            end
            
            if isKey(eqCOMDupireSpotGF.modelParams,'deltaCutOff')
                eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            else
                eqCOMDupireSpotGF.deltaCutOff = 0.0;
            end
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrike')
                settleFuturesRef = eqCOMDupireSpotGF.settleFuturesRef;
               
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)- fwd;
                        
                        if fwdMoneyness(k,j) <= 0.0
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
%                         blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                          blackOTMVega(k,j) = black.NormalVanillaFwdVega(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j));
                   end
                end
                
            elseif strcmp(volSurface.params('moneyNessType'),'fixedStrikeOneStep')
                settleFuturesRefSpot = eqCOMDupireSpotGF.modelParams('settleFuturesRefSpot');
%                 eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRefSpot(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            elseif strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess')
                settleFuturesRef = eqCOMDupireSpotGF.settleFuturesRef;
                
                
                for k=1:expirySize
                    
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = settleFuturesRef(k)*strike(j);
                        
                        if fwdMoneyness(k,j) <= 0
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'P');
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'C');
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        
                        blackOTMVega(k,j) = black.NormalVanillaFwdVega(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j));
%                         blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR')  %% SSR
                for k=1:expirySize
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = volSurface.fwdMoneyness(k,j);
                        
                        
                        if fwdMoneyness(k,j) <= 0
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'P');
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.NormalVanillaFwd(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j),'C');
%                             blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = black.NormalVanillaFwdVega(expiry(k),0.0,fwdMoneyness(k,j),blackVol(k,j));
%                         blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        if strike(j) <= 0
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        else
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        end

                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'P');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'C');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        end
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                         
                    end
                    dfOut(k) = black.zeroCurve.DF(expiry(k)/365.0);
                end
                
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            
          %% Grid Generation for Vol Calibration Start
            % vol proxy calibration grid setting
            if strcmp(eqCOMDupireSpotGF.gridType,'uniform')
                params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
                params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
                params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
    %             params.dK   = eqCOMDupireSpotGF.modelParams('dK');
    %             params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');

                dK = (params.Kmax - params.Kmin)/(params.Ns-1);
                params.dK = dK;

                Ks = zeros(params.Ns,1);
                for i=1:params.Ns
                    Ks(i) = params.Kmin + dK*(i-1);
                end

                params.Ks = Ks;
                % current spot on the grid
    %             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
                params.Pricingidx = floor((0.0-params.Ks(1))/params.dK) + 1;
            else
                params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
                params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
                params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
    
                dK = (asinh(params.Kmax) - asinh(params.Kmin))/(params.Ns-1);
                params.dK = dK;

                Ks = zeros(params.Ns,1);
                for i=1:params.Ns
                    Ks(i) = sinh(asinh(params.Kmin) + dK*(i-1));
                end

                params.Ks = Ks;
                % current spot on the grid
    %             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
                params.Pricingidx = floor((0.0-asinh(params.Ks(1)))/params.dK) + 1;
                
            end
          %% Grid Generation End
          
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            initProb = zeros(1,params.Ns);
            initProb(params.Pricingidx) = 1.0;
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.rmseTotal1 = 0;
            out.fwdVolMseTotal1 = 0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            out.lnModelVol(i,j) =  LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.modelImpVol(i,j),params.expiry(i)/365.0);
                            out.lnMarketVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.marketImpVol(i,j),params.expiry(i)/365.0);
                            out.lnVolError(i,j) = out.lnModelVol(i,j) - out.lnMarketVol(i,j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    out.fwdLnVolMseTotal = 0.0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if out.useYN(j,k)
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                out.fwdLnVolMseTotal = out.fwdLnVolMseTotal + out.lnVolError(j,k)*out.lnVolError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    out.fwdLnVolMseTotal = sqrt(out.fwdLnVolMseTotal/N);
%                     toc
                    
%                     tic
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    params.marketStrikes = out.marketStrikes;
                    
%                     toc
                    
%                     calculate backward scheme for given target
%                     compareforwardMCFlag = 1 for one step euler scheme
%                     compareforwardMCFlag = 2 for daily euler scheme
%                     
%                     compareforwardMCFlag = 3 for markov chain monte carlo
                     
                    
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= 0.0
                                    out.backwardVol(i,j) = BisecNormIV('P',0.0,out.marketStrikes(i,j),0,expiry(i)/365.0,0.0001,1000,out.pdeOTMPrices(i,j),1e-10,10000);
                                    out.bacwardLnVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.backwardVol(i,j),expiry(i)/365.0);
%                                     out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = BisecNormIV('C',0.0,out.marketStrikes(i,j),0,expiry(i)/365.0,0.0001,1000,out.pdeOTMPrices(i,j),1e-10,10000);
                                    out.bacwardLnVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.backwardVol(i,j),expiry(i)/365.0);
%                                     out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);
                                out.backLnVolError(i,j) = out.bacwardLnVol(i,j) - out.lnMarketVol(i,j);

                            end
                        end

                        N=0;
                        out.backLnVolMseTotal = 0.0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if out.useYN(j,k)
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    out.backLnVolMseTotal = out.backLnVolMseTotal + out.backLnVolError(j,k)*out.backLnVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        out.backLnVolMseTotal=sqrt(out.backLnVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=0.0
                                    out.backwardVol(i,j) = BisecNormIV('P',0.0,out.marketStrikes(i,j),0,expiry(i)/365.0,0.0001,1000,out.mcOTMPrices(i,j),1e-10,10000);
                                    out.bacwardLnVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.backwardVol(i,j),expiry(i)/365.0);
%                                     out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = BisecNormIV('C',0.0,out.marketStrikes(i,j),0,expiry(i)/365.0,0.0001,1000,out.mcOTMPrices(i,j),1e-10,10000);
                                    out.bacwardLnVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.backwardVol(i,j),expiry(i)/365.0);
%                                     out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);
                                out.backLnVolError(i,j) = out.bacwardLnVol(i,j) - out.lnMarketVol(i,j);

                            end
                        end

                        N=0;
                        out.backLnVolMseTotal = 0.0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if out.useYN(j,k)
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    out.backLnVolMseTotal = out.backLnVolMseTotal + out.backLnVolError(j,k)*out.backLnVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        out.backLnVolMseTotal=sqrt(out.backLnVolMseTotal/N);
                        
                    elseif pricingSchemeType == 5
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotalTest(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=0.0
                                    out.backwardVol(i,j) = BisecNormIV('P',0.0,out.marketStrikes(i,j),0,expiry(i)/365.0,0.0001,1000,out.mcOTMPrices(i,j),1e-10,10000);
                                    out.bacwardLnVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.backwardVol(i,j),expiry(i)/365.0);
%                                     out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = BisecNormIV('C',0.0,out.marketStrikes(i,j),0,expiry(i)/365.0,0.0001,1000,out.mcOTMPrices(i,j),1e-10,10000);
                                    out.bacwardLnVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.backwardVol(i,j),expiry(i)/365.0);
%                                     out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);
                                out.backLnVolError(i,j) = out.bacwardLnVol(i,j) - out.lnMarketVol(i,j);

                            end
                        end

                        N=0;
                        out.backLnVolMseTotal = 0.0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if out.useYN(j,k)
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    out.backLnVolMseTotal = out.backLnVolMseTotal + out.backLnVolError(j,k)*out.backLnVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        out.backLnVolMseTotal=sqrt(out.backLnVolMseTotal/N);
                        
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end

%                     toc

                case 'bootstrapComputeTargetVol'
                    
                    %                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            out.lnModelVol(i,j) =  LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.modelImpVol(i,j),params.expiry(i)/365.0);
                            out.lnMarketVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.marketImpVol(i,j),params.expiry(i)/365.0);
                            out.lnVolError(i,j) = out.lnModelVol(i,j) - out.lnMarketVol(i,j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    out.fwdLnVolMseTotal = 0.0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if out.useYN(j,k)
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                out.fwdLnVolMseTotal = out.fwdLnVolMseTotal + out.lnVolError(j,k)*out.lnVolError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    out.fwdLnVolMseTotal = sqrt(out.fwdLnVolMseTotal/N);
%                     toc
                    
%                     tic
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    params.marketStrikes = out.marketStrikes;
                    
                  %% compute implied surface for targetStrikes;
                    
                    targetExpiry = params.expiry;
                    % targetStrike
                    targetStrikesReduced = 0.5:0.1:1.5;
                    for i=1:length(targetExpiry)
                        nmFwd = eqCOMDupireSpotGF.settleFuturesRef(i);
                        for j=1:size(targetStrikesReduced,2)
                            targetStrikes(i,j) = nmFwd*targetStrikesReduced(j) - nmFwd;
                        end
                    end
                    
                    eqCOMDupireSpotGF.targetStrikes = targetStrikes;
                    
                    out.targetStrikes = targetStrikes;
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVol = outDummy.impVolSurface;
                    out.cValueSurface = outDummy.cValueSurface;
                    out.pValueSurface = outDummy.pValueSurface;
                    out.probMeshInt = outDummy.probMeshInt;
                    
                    
                    % construct new implied volSurface and calibrate on
                    % this surface
%                     origMktData = eqCOMDupireSpotGF.mktData;
%                     
%                     originalVolSurfaceData = origMktData('impliedVolSurface').params('rawData');
%                     
%                     
%                     
%                     newVolSurfaceData = originalVolSurfaceData;
%                     newVolSurfaceData(2:size(newVolSurfaceData,1),2:size(newVolSurfaceData,2)) = outDummy.impVolSurface(:,:);
%                     
%                     mktData = eqCOMDupireSpotGF.mktData('impliedVolSurface').params;
%                     
%                     if isKey(mktData,'parametrization')
%                         mktData('parametrization') = 'nonParametric';
%                     end
%                     
%                     mktData('rawData') = newVolSurfaceData;
%                     mktData('fwdMoneyness') = out.fwdMoneyness;
%                     impliedVolSurfaceMktData = MktData(mktData);
%                     impliedVolSurface = EQVolSurface(impliedVolSurfaceMktData);
%                     impliedVolSurface.params('moneyNessType') = 'fwdMoneyNessSSR';
%                     origMktData('impliedVolSurface') = impliedVolSurface;
%                     
%                     newBlack =  EQBlack(EQModel(Model(origMktData,black.modelParams)));
%                     
%                     newOut = eqCOMDupireSpotGF.CalibrateToVolSurface(newBlack,'bootstrapForwardOnly');
% %                     newOut = eqCOMDupireSpotGF.CalibrateToVolSurface(newBlack,'bootstrap');
%                     
%                     % 1st step calibration info
%                     newOut.rmseTotal1 = out.rmseTotal1;
%                     newOut.fwdVolMseTotal1 = out.fwdVolMseTotal1;
%                     newOut.originalUseYN = out.useYN;
%                     
%                     % bumped volSurface as output
%                     % originalOut 20181226
%                     newOut.originalImpVolSurface = out.marketImpVol;
%                     newOut.originalModelImpVol = out.modelImpVol;
%                     newOut.originalVolProxy = out.volProxy;
%                     newOut.originalMarketStrikes = out.marketStrikes;
%                     
%                     newOut.shiftedImpVolSurface = outDummy.impVolSurface;
%                     newOut.targetStrikes = targetStrikes;
%                     
%                     out = newOut;
%                     
%                     
%                     
%                     out = newOut;
                    aaa = 1.0;
                    
                case 'bootstrapForwardSSR'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            out.lnModelVol(i,j) =  LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.modelImpVol(i,j),params.expiry(i)/365.0);
                            out.lnMarketVol(i,j) = LNVolFromNVol(settleFuturesRef(i),settleFuturesRef(i) + out.marketStrikes(i,j),out.marketImpVol(i,j),params.expiry(i)/365.0);
                            out.lnVolError(i,j) = out.lnModelVol(i,j) - out.lnMarketVol(i,j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    out.fwdLnVolMseTotal = 0.0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            % we report only those calibrated target only
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal1 = out.rmseTotal1 + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal1 = out.fwdVolMseTotal1 + out.volError(j,k)*out.volError(j,k);
                                out.fwdLnVolMseTotal = out.fwdLnVolMseTotal + out.lnVolError(j,k)*out.lnVolError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal1 = sqrt(out.rmseTotal1/N);
                    out.fwdVolMseTotal1 = sqrt(out.fwdVolMseTotal1/N);
                    out.fwdLnVolMseTotal = sqrt(out.fwdLnVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    % compute Target implied vol
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                  %% compute implied surface for targetStrikes;
                    if ~isKey(eqCOMDupireSpotGF.modelParams,'slopeTerm')
                       eqCOMDupireSpotGF.slopeTerm = ones(length(out.expiry),1)*1.0;
                    else
                       eqCOMDupireSpotGF.slopeTerm =  eqCOMDupireSpotGF.modelParams('slopeTerm');
                    end
                    
                    targetExpiry = params.expiry;
                    targetStrikes = out.fwdMoneyness;
%                     slope = eqCOMDupireSpotGF.slope;
                  %% normal vol Smile Dynamics
                    for i=1:length(targetExpiry)
                        slope = eqCOMDupireSpotGF.slopeTerm(i);
                        nmFwd = eqCOMDupireSpotGF.FwdNM(targetExpiry(i));
                        referenceNmFwd = eqCOMDupireSpotGF.ReferenceFwdNM(targetExpiry(i));
                        for j=1:size(targetStrikes,2)
                            targetStrikes(i,j) = out.fwdMoneyness(i,j) + slope*(nmFwd - referenceNmFwd);
                        end
                    end
                    
                    eqCOMDupireSpotGF.targetStrikes = targetStrikes;
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVol = outDummy.impVolSurface;
                    out.cValueSurface = outDummy.cValueSurface;
                    out.pValueSurface = outDummy.pValueSurface;
                    out.probMeshInt = outDummy.probMeshInt;
                    
                    % construct new implied volSurface and calibrate on
                    % this surface
                    origMktData = eqCOMDupireSpotGF.mktData;
                    
                    originalVolSurfaceData = origMktData('impliedVolSurface').params('rawData');
                    
                    
                    
                    newVolSurfaceData = originalVolSurfaceData;
                    newVolSurfaceData(2:size(newVolSurfaceData,1),2:size(newVolSurfaceData,2)) = outDummy.impVolSurface(:,:);
                    
                    mktData = eqCOMDupireSpotGF.mktData('impliedVolSurface').params;
                    
                    if isKey(mktData,'parametrization')
                        mktData('parametrization') = 'nonParametric';
                    end
                    
                    mktData('rawData') = newVolSurfaceData;
                    mktData('fwdMoneyness') = out.fwdMoneyness;
                    impliedVolSurfaceMktData = MktData(mktData);
                    impliedVolSurface = EQVolSurface(impliedVolSurfaceMktData);
                    impliedVolSurface.params('moneyNessType') = 'fwdMoneyNessSSR';
                    origMktData('impliedVolSurface') = impliedVolSurface;
                    
                  %% EQ Bachelier Model to calibrate market PlainVanilla Options
                    newBlack = EQBachelier(EQModel(Model(origMktData,black.modelParams))); 
%                     newBlack =  EQBlack(EQModel(Model(origMktData,black.modelParams)));
                    
                    newOut = eqCOMDupireSpotGF.CalibrateToVolSurface(newBlack,'bootstrapForwardOnly');
%                     newOut = eqCOMDupireSpotGF.CalibrateToVolSurface(newBlack,'bootstrap');
                    
                    % 1st step calibration info
                    newOut.rmseTotal1 = out.rmseTotal1;
                    newOut.fwdVolMseTotal1 = out.fwdVolMseTotal1;
                    newOut.originalUseYN = out.useYN;
                    
                    % bumped volSurface as output
                    % originalOut 20181226
                    newOut.originalImpVolSurface = out.marketImpVol;
                    newOut.originalModelImpVol = out.modelImpVol;
                    newOut.originalVolProxy = out.volProxy;
                    newOut.originalMarketStrikes = out.marketStrikes;
                    
                    newOut.shiftedImpVolSurface = outDummy.impVolSurface;
                    newOut.targetStrikes = targetStrikes;
                    
                    out = newOut;
                    
                    
                    
                    out = newOut;
                    aaa = 1.0;
                    
                case 'bootstrapFixedStrikeOneStep'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    
                    for j=1:expirySize
                        for k=1:strikeSize
                            % we report only those calibrated target only
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal1 = out.rmseTotal1 + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal1 = out.fwdVolMseTotal1 + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal1 = sqrt(out.rmseTotal1/N);
                    out.fwdVolMseTotal1 = sqrt(out.fwdVolMseTotal1/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    % compute Target implied vol
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                  %% compute implied surface for targetStrikes;
%                     
%                     targetExpiry = params.expiry;
%                     targetStrikes = out.fwdMoneyness;
%                     slope = eqCOMDupireSpotGF.slope;
%                     for i=1:length(targetExpiry)
%                         nmFwd = eqCOMDupireSpotGF.FwdNM(targetExpiry(i));
%                         referenceNmFwd = eqCOMDupireSpotGF.ReferenceFwdNM(targetExpiry(i));
%                         for j=1:size(targetStrikes,2)
%                             targetStrikes(i,j) = out.fwdMoneyness(i,j)*(1.0 + slope*(nmFwd/referenceNmFwd - 1.0));
%                         end
%                     end
%                     
%                     eqCOMDupireSpotGF.targetStrikes = targetStrikes;
%                     
%                     outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
%                     out.forwardImpVol = outDummy.impVolSurface;
%                     out.cValueSurface = outDummy.cValueSurface;
%                     out.pValueSurface = outDummy.pValueSurface;
%                     out.probMeshInt = outDummy.probMeshInt;
%                     
%                     % construct new implied volSurface and calibrate on
%                     % this surface
%                     origMktData = eqCOMDupireSpotGF.mktData;
%                     
%                     originalVolSurfaceData = origMktData('impliedVolSurface').params('rawData');
%                     
%                     
%                     
%                     newVolSurfaceData = originalVolSurfaceData;
%                     newVolSurfaceData(2:size(newVolSurfaceData,1),2:size(newVolSurfaceData,2)) = outDummy.impVolSurface(:,:);
%                     
%                     mktData = eqCOMDupireSpotGF.mktData('impliedVolSurface').params;
%                     
%                     if isKey(mktData,'parametrization')
%                         mktData('parametrization') = 'nonParametric';
%                     end
%                     
%                     mktData('rawData') = newVolSurfaceData;
%                     mktData('fwdMoneyness') = out.fwdMoneyness;
%                     impliedVolSurfaceMktData = MktData(mktData);
%                     impliedVolSurface = EQVolSurface(impliedVolSurfaceMktData);
%                     impliedVolSurface.params('moneyNessType') = 'fwdMoneyNessSSR';
%                     origMktData('impliedVolSurface') = impliedVolSurface;
%                     
%                     newBlack =  EQBlack(EQModel(Model(origMktData,black.modelParams)));
%                     
%                     newOut = eqCOMDupireSpotGF.CalibrateToVolSurface(newBlack,'bootstrapForwardOnly');
% %                     newOut = eqCOMDupireSpotGF.CalibrateToVolSurface(newBlack,'bootstrap');
%                     
%                     % 1st step calibration info
%                     newOut.rmseTotal1 = out.rmseTotal1;
%                     newOut.fwdVolMseTotal1 = out.fwdVolMseTotal1;
%                     newOut.originalUseYN = out.useYN;
%                     
%                     % bumped volSurface as output
%                     % originalOut 20181226
%                     newOut.originalImpVolSurface = out.marketImpVol;
%                     newOut.originalModelImpVol = out.modelImpVol;
%                     newOut.originalVolProxy = out.volProxy;
%                     newOut.originalMarketStrikes = out.marketStrikes;
%                     
%                     newOut.shiftedImpVolSurface = outDummy.impVolSurface;
%                     newOut.targetStrikes = targetStrikes;
%                     
%                     out = newOut;
%                     
%                     
%                     
%                     out = newOut;
%                     aaa = 1.0;
                case 'bootstrapForwardOnlyDebug'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    %% SSR
                    out.targetStrikes = eqCOMDupireSpotGF.targetStrikes;
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    targetExpiry = params.expiry;
                    dummyStrikes = [0.5:0.1:1.5];
                    targetStrikes = repmat(dummyStrikes,[length(targetExpiry), 1]);
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    forwardImpVolSurf = outDummy.impVolSurface;
                    
                    
                    useATMQuantoInput = eqCOMDupireSpotGF.modelParams('useATMQuantoInput');
                    if useATMQuantoInput
                        eqCOMDupireSpotGF.atmForwardVol = eqCOMDupireSpotGF.modelParams('atmForwardVol');
                        
                        %unique & union termStructures of fxVol & impVol
                        sigmaTimes = unique(union(eqCOMDupireSpotGF.atmForwardVol(:,1),eqCOMDupireSpotGF.quantoFXVol(:,1)));
                        sigmaTimes = sort(sigmaTimes,'ascend');
                        sigmaTimesSize = length(sigmaTimes);
                        atmForwardVolNew = zeros(sigmaTimesSize,2);
                        quantoFXVolNew = zeros(sigmaTimesSize,2);

                        atmForwardVolNew(:,1) = sigmaTimes;
                        quantoFXVolNew(:,1) = sigmaTimes;

                        for idxJJ = 1:sigmaTimesSize
                            atmForwardVolNew(idxJJ,2) = H_interpolation(eqCOMDupireSpotGF.atmForwardVol(:,1),eqCOMDupireSpotGF.atmForwardVol(:,2),sigmaTimes(idxJJ),0);
                            quantoFXVolNew(idxJJ,2) = H_interpolation(eqCOMDupireSpotGF.quantoFXVol(:,1),eqCOMDupireSpotGF.quantoFXVol(:,2),sigmaTimes(idxJJ),0); 
                        end

                        eqCOMDupireSpotGF.atmForwardVolNew = atmForwardVolNew;
                        eqCOMDupireSpotGF.quantoFXVolNew   = quantoFXVolNew;
                        eqCOMDupireSpotGF.sigmaTimes = sigmaTimes;
                        
                    else
                        %compute atmImpVol From VolSurface
                        %mid Idx is 6 be careful !!
                        atmImpVolRaw = forwardImpVolSurf(:,6);
                        atmForwardVolRaw = zeros(length(targetExpiry),1);

                        %bootStrapping ATM ImpVol
                        atmForwardVolRaw(1) = atmImpVolRaw(1);
                        for idxJJ=2:length(targetExpiry)
                            forwardVar = atmImpVolRaw(idxJJ)*atmImpVolRaw(idxJJ)*targetExpiry(idxJJ)/365.0;
                            currentVar = atmImpVolRaw(idxJJ-1)*atmImpVolRaw(idxJJ-1)*targetExpiry(idxJJ-1)/365.0;
                            dTVar = (targetExpiry(idxJJ) - targetExpiry(idxJJ-1))/365.0;
                            atmForwardVolRaw(idxJJ) = sqrt((forwardVar - currentVar)/dTVar);
                        end
                        out.atmForwardVol = zeros(length(targetExpiry),2);
                        out.atmForwardVol(:,1) = targetExpiry;
                        out.atmForwardVol(:,2) = atmForwardVolRaw;
                        eqCOMDupireSpotGF.atmForwardVol = out.atmForwardVol;

                        %unique & union termStructures of fxVol & impVol
                        sigmaTimes = unique(union(eqCOMDupireSpotGF.atmForwardVol(:,1),eqCOMDupireSpotGF.quantoFXVol(:,1)));
                        sigmaTimes = sort(sigmaTimes,'ascend');
                        sigmaTimesSize = length(sigmaTimes);
                        atmForwardVolNew = zeros(sigmaTimesSize,2);
                        quantoFXVolNew = zeros(sigmaTimesSize,2);

                        atmForwardVolNew(:,1) = sigmaTimes;
                        quantoFXVolNew(:,1) = sigmaTimes;

                        for idxJJ = 1:sigmaTimesSize
                            atmForwardVolNew(idxJJ,2) = H_interpolation(eqCOMDupireSpotGF.atmForwardVol(:,1),eqCOMDupireSpotGF.atmForwardVol(:,2),sigmaTimes(idxJJ),0);
                            quantoFXVolNew(idxJJ,2) = H_interpolation(eqCOMDupireSpotGF.quantoFXVol(:,1),eqCOMDupireSpotGF.quantoFXVol(:,2),sigmaTimes(idxJJ),0); 
                        end

                        eqCOMDupireSpotGF.atmForwardVolNew = atmForwardVolNew;
                        eqCOMDupireSpotGF.quantoFXVolNew   = quantoFXVolNew;
                        eqCOMDupireSpotGF.sigmaTimes = sigmaTimes;
                    end
                    
                    targetExpiry2 = repmat(targetExpiry,[1, length(dummyStrikes)]);
                    
                    totalVar = forwardImpVolSurf.*forwardImpVolSurf.*targetExpiry2/365.0;
                    
                    diffVar = zeros(length(targetExpiry)-1,length(dummyStrikes));
                    arbitrageCheckMat = zeros((length(targetExpiry)-1)*length(dummyStrikes),1);
                    
                    for idxzz=1:length(targetExpiry)-1
                        diffVar(idxzz,:) = totalVar(idxzz+1,:)-totalVar(idxzz,:);
                    end
                    
                                        
                    arbitrageCheckSum = 0;
                    for idxzz=1:length(targetExpiry)-1
                        for idxww= 1:length(dummyStrikes)
                            if diffVar(idxzz,idxww) < 0
                                arbitrageCheckMat((idxzz-1)*(length(dummyStrikes))+ idxww,1) = 1;
                                arbitrageCheckSum = arbitrageCheckSum +1;
                            end
                            
                        end
                    end
                    
                    out.arbitrageCheckMat = arbitrageCheckMat;
                    out.arbitrageCheckSum = arbitrageCheckSum;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                  
                  
                    aaa = 1.0;
                    
                    
                case 'bootstrapForwardOnlyDebugUseYNFree'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    %% SSR
                    out.targetStrikes = eqCOMDupireSpotGF.targetStrikes;
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    targetExpiry = params.expiry;
                    dummyStrikes = [0.5:0.1:1.5];
                    targetStrikes = repmat(dummyStrikes,[length(targetExpiry), 1]);
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    forwardImpVolSurf = outDummy.impVolSurface;
                    
                    
                    useATMQuantoInput = eqCOMDupireSpotGF.modelParams('useATMQuantoInput');
                    if useATMQuantoInput
                        eqCOMDupireSpotGF.atmForwardVol = eqCOMDupireSpotGF.modelParams('atmForwardVol');
                        
                        %unique & union termStructures of fxVol & impVol
                        sigmaTimes = unique(union(eqCOMDupireSpotGF.atmForwardVol(:,1),eqCOMDupireSpotGF.quantoFXVol(:,1)));
                        sigmaTimes = sort(sigmaTimes,'ascend');
                        sigmaTimesSize = length(sigmaTimes);
                        atmForwardVolNew = zeros(sigmaTimesSize,2);
                        quantoFXVolNew = zeros(sigmaTimesSize,2);

                        atmForwardVolNew(:,1) = sigmaTimes;
                        quantoFXVolNew(:,1) = sigmaTimes;

                        for idxJJ = 1:sigmaTimesSize
                            atmForwardVolNew(idxJJ,2) = H_interpolation(eqCOMDupireSpotGF.atmForwardVol(:,1),eqCOMDupireSpotGF.atmForwardVol(:,2),sigmaTimes(idxJJ),0);
                            quantoFXVolNew(idxJJ,2) = H_interpolation(eqCOMDupireSpotGF.quantoFXVol(:,1),eqCOMDupireSpotGF.quantoFXVol(:,2),sigmaTimes(idxJJ),0); 
                        end

                        eqCOMDupireSpotGF.atmForwardVolNew = atmForwardVolNew;
                        eqCOMDupireSpotGF.quantoFXVolNew   = quantoFXVolNew;
                        eqCOMDupireSpotGF.sigmaTimes = sigmaTimes;
                        
                    else
                        %compute atmImpVol From VolSurface
                        %mid Idx is 6 be careful !!
                        atmImpVolRaw = forwardImpVolSurf(:,6);
                        atmForwardVolRaw = zeros(length(targetExpiry),1);

                        %bootStrapping ATM ImpVol
                        atmForwardVolRaw(1) = atmImpVolRaw(1);
                        for idxJJ=2:length(targetExpiry)
                            forwardVar = atmImpVolRaw(idxJJ)*atmImpVolRaw(idxJJ)*targetExpiry(idxJJ)/365.0;
                            currentVar = atmImpVolRaw(idxJJ-1)*atmImpVolRaw(idxJJ-1)*targetExpiry(idxJJ-1)/365.0;
                            dTVar = (targetExpiry(idxJJ) - targetExpiry(idxJJ-1))/365.0;
                            atmForwardVolRaw(idxJJ) = sqrt((forwardVar - currentVar)/dTVar);
                        end
                        out.atmForwardVol = zeros(length(targetExpiry),2);
                        out.atmForwardVol(:,1) = targetExpiry;
                        out.atmForwardVol(:,2) = atmForwardVolRaw;
                        eqCOMDupireSpotGF.atmForwardVol = out.atmForwardVol;

                        %unique & union termStructures of fxVol & impVol
                        sigmaTimes = unique(union(eqCOMDupireSpotGF.atmForwardVol(:,1),eqCOMDupireSpotGF.quantoFXVol(:,1)));
                        sigmaTimes = sort(sigmaTimes,'ascend');
                        sigmaTimesSize = length(sigmaTimes);
                        atmForwardVolNew = zeros(sigmaTimesSize,2);
                        quantoFXVolNew = zeros(sigmaTimesSize,2);

                        atmForwardVolNew(:,1) = sigmaTimes;
                        quantoFXVolNew(:,1) = sigmaTimes;

                        for idxJJ = 1:sigmaTimesSize
                            atmForwardVolNew(idxJJ,2) = H_interpolation(eqCOMDupireSpotGF.atmForwardVol(:,1),eqCOMDupireSpotGF.atmForwardVol(:,2),sigmaTimes(idxJJ),0);
                            quantoFXVolNew(idxJJ,2) = H_interpolation(eqCOMDupireSpotGF.quantoFXVol(:,1),eqCOMDupireSpotGF.quantoFXVol(:,2),sigmaTimes(idxJJ),0); 
                        end

                        eqCOMDupireSpotGF.atmForwardVolNew = atmForwardVolNew;
                        eqCOMDupireSpotGF.quantoFXVolNew   = quantoFXVolNew;
                        eqCOMDupireSpotGF.sigmaTimes = sigmaTimes;
                    end
                    
                    targetExpiry2 = repmat(targetExpiry,[1, length(dummyStrikes)]);
                    
                    totalVar = forwardImpVolSurf.*forwardImpVolSurf.*targetExpiry2/365.0;
                    
                    diffVar = zeros(length(targetExpiry)-1,length(dummyStrikes));
                    arbitrageCheckMat = zeros((length(targetExpiry)-1)*length(dummyStrikes),1);
                    
                    for idxzz=1:length(targetExpiry)-1
                        diffVar(idxzz,:) = totalVar(idxzz+1,:)-totalVar(idxzz,:);
                    end
                    
                                        
                    arbitrageCheckSum = 0;
                    for idxzz=1:length(targetExpiry)-1
                        for idxww= 1:length(dummyStrikes)
                            if diffVar(idxzz,idxww) < 0
                                arbitrageCheckMat((idxzz-1)*(length(dummyStrikes))+ idxww,1) = 1;
                                arbitrageCheckSum = arbitrageCheckSum +1;
                            end
                            
                        end
                    end
                    
                    out.arbitrageCheckMat = arbitrageCheckMat;
                    out.arbitrageCheckSum = arbitrageCheckSum;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                  
                  
                    aaa = 1.0;      

%                     
                case 'bootstrapForwardOnly'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        fwdDummy = eqCOMDupireSpotGF.FwdNM(params.expiry(i));
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            out.lnModelVol(i,j) =  LNVolFromNVol(fwdDummy,fwdDummy + out.marketStrikes(i,j),out.modelImpVol(i,j),params.expiry(i)/365.0);
                            out.lnMarketVol(i,j) = LNVolFromNVol(fwdDummy,fwdDummy + out.marketStrikes(i,j),out.marketImpVol(i,j),params.expiry(i)/365.0);
                            out.lnVolError(i,j) = out.lnModelVol(i,j) - out.lnMarketVol(i,j);

                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    out.fwdLnVolMseTotal = 0.0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                out.fwdLnVolMseTotal = out.fwdLnVolMseTotal + out.lnVolError(j,k)*out.lnVolError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    out.fwdLnVolMseTotal = sqrt(out.fwdLnVolMseTotal/N);
                    toc
                    
                    %% SSR
                    out.targetStrikes = eqCOMDupireSpotGF.targetStrikes;
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                  
                  
                    aaa = 1.0;
                    
                    
                      

                otherwise
                    disp('unImplemented')
                    
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMFLSimpleSettle < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        %Likely
        settleFuturesRef
        
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMFLSimpleSettle(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            localVol = interp1(volProxyKs,volProxy,Ks','linear','extrap');
            
%             for i=1:length(Ks)
%                 localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
%             end   
                
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           if strcmp(eqCOMDupireSpotGF.modelParams('useSettleFuturesYN'),'YES')
               dummyExpiry = eqCOMDupireSpotGF.mktData('impliedVolSurface').maturities;
               refFuturesCurve = zeros(length(dummyExpiry),2);
               
               if strcmp(optParams.params.volProxyRefYN,'YES') 
                   dummyExpiry = eqCOMDupireSpotGF.modelParams('settleFuturesRefDays');
                   dummyData = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                   refFuturesCurve(:,1) = dummyExpiry;
                   refFuturesCurve(:,2) = dummyData;
               else
                   dummyExpiry = eqCOMDupireSpotGF.modelParams('settleFuturesSpotDays');
                   dummyData = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                   refFuturesCurve(:,1) = dummyExpiry;
                   refFuturesCurve(:,2) = dummyData;
               end
               
           else
               if strcmp(optParams.params.volProxyRefYN,'YES') 
                   refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
               else
                   refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
               end
           end
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
               
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           dK = optParams.dK;
           priceC = fwdPriceC;
           priceP = fwdPRiceP;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        priceC,priceP,optParams);

               priceC = outGF.newPriceC;
               priceP = outGF.newPriceP;
               
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = priceC;
                   dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                       priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                       priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                       priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);
                       
                       if priceC(idxzz) < 0
                            priceC(idxzz) = 0.0;
                       end
                       
                       if priceP(idxzz) < 0
                           priceP(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           out.fwdPriceCOut = priceC;
           out.fwdPricePOut = priceP;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,priceC,priceP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(priceC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(priceC);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newPriceC = A_exp1*priceC;
                newPriceP = A_exp1*priceP;
            
            end
            
            out.newPriceC = newPriceC;
            out.newPriceP = newPriceP;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)*(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)*(1.0 + dividendRatio)-Ks(NGP))/dK;
                       lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       
                       if lastPrice(idxzz) < 0
                            lastPrice(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYNFlag);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1),volProxyRefYN);
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            if strcmp(volProxyRefYNFlag,'YES')
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxyRef(idxNow,:);
            else
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            end
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            
            volProxy   = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            volProxyKs = eqCOMDupireSpotGF.localVolSurface.marketStrikes(idxNow,:);
            
            localVol = interp1(volProxyKs,volProxy,x','linear','extrap');
            
            
%             localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
%             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
%             
            
%             for ii =1:length(x)
%                 localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
%             end
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,...
                        lastProb,lastPriceC, lastPriceP,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            
            nextProb = lastProb*condProb;
            nextPriceC = condProb*lastPriceC;
            % Check the ex-dividend date & if it is then adjust prob accordingly 
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               dummyProb = nextProb;
               dummyC = nextPriceC; 
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;

               if dividendRatio > 0
                   
               end
               for  idxzz= 1:length(dummyProb)
                   NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                   if NGP < 1
                       NGP = 1;
                   end

                   if NGP > length(dummyC)-1
                       NGP = length(dummyC)-1;
                   end

                   weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                   priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                   priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                   priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                   priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);

                   if priceC(idxzz) < 0
                        priceC(idxzz) = 0.0;
                   end

                   if priceP(idxzz) < 0
                       priceP(idxzz) = 0.0;
                   end

               end
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalCumPerExpiry(nextProb,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nPoints = length(Ks);
            
            debugDx = zeros(NMC,1);
            debugIdx1 = zeros(NMC,1);
            debugIdx2 = zeros(NMC,1);
            debugWeight1 = zeros(NMC,1);
            debugWeight2 = zeros(NMC,1);
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                
                idxH1 = min(find(uSample(i) < cumProb1));
                idxH2 = min(find(uSample(i) < cumProb2));
                debugDx(i) = idxH1-idxH2;
                debugIdx1(i) = idxH1;
                debugIdx2(i) = idxH2;
                
                nextX = (1.0-lastXWeight(i))*Ks(idxH1) + lastXWeight(i)*Ks(idxH2);
                idxDummy = find(nextX < Ks);
                if isempty(idxDummy)
                    error('nextX is not covered in the grid K')
                end
                
                idxDummyS = min(idxDummy);
                weight = (Ks(idxDummyS)-nextX)/dK;
                nextXIdx(i) = idxDummyS;
                nextXWeight(i) = weight;
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;

            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardLikely(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
            
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
%            %% renormalize Radon Nikodym Derivatives 
%             if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                 avgLHR = mean(likelyHoodRatio);
%                 likelyHoodRatio = likelyHoodRatio/avgLHR;
%             end
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
            %% importtant correction above
            
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   
                 %% dividendRatioRef start
                   if nextXIdxRef(i) ==1 
                       nextXRef = Ks(nextXIdxRef(i));
                   else
                       nextXRef = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextXRef = nextXRef*(1.0 + dividendRatioRef);
                   idxDummyRef = find(nextXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - nextXRef)/dK;
                       end
                   end

                   out.nextXIdxRef(i) = idxDummySRef;
                   out.nextXWeightRef(i) = weightRef;
                 
                 %% dividendRatioRef end
                 
                   if nextXIdxRef(i) ==1 
                       nextX = Ks(nextXIdxRef(i));
                   else
                       nextX = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == 1
                    nextXWeight(i) = 0.0;
                else

                    sampleZ = uSample(i);
                    
                    nextXWeight(i) = (cumProb(idxH1) -sampleZ)/(cumProb(idxH1)-cumProb(idxH1-1));
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyP)
                       predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            if strcmp(params.params.volProxyRefYN,'YES')
                settleFutures = eqCOMDupireSpotGF.settleFuturesRef;
            else
                settleFutures = eqCOMDupireSpotGF.settleFutures;
            end
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            cValue = fwdPriceCNew;
            pValue = fwdPricePNew;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffLikely(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
            cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
            if idx ~= 1 
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                        cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    end
                end
              
                
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*cumulativeLikelyHoodRatio(idx11);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
                
            end    
            
            
        end
      
        function columnOut = MCPayoffLikelyRen(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
           %% sum(cumLHR2) = N - sum(cumLHR1); 
            cumulativeLikelyHoodRatio = zeros(modelStatesSize,1);
            
            dumMeasureSum = 0.0;
            dumMeasureSumPrev = 0.0;
            dumMeasureN = 0;
            if idx == 1 
                cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
                dumMeasureSum = sum(cumulativeLikelyHoodRatio);
                cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/dumMeasureSum*modelStatesSize;
                columnOut.cumLHR(:,idx) = cumulativeLikelyHoodRatio;
            else
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % dead path
                        dumMeasureSumPrev = dumMeasureSumPrev + columnIn.cumLHR(idx11,idx-1);
                        dumMeasureN = dumMeasureN + 1;
                    end
                end
                
                if dumMeasureN < modelStatesSize % if alive path normalize the relative measure
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                            dumMeasureSum = dumMeasureSum + cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                    
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = cumulativeLikelyHoodRatio(idx11)/(dumMeasureSum)*(modelStatesSize - dumMeasureSumPrev);
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                
                for idx11 =1:modelStatesSize % 1st early redemption
                        % every path is an alive path use all path to
                       
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                end
                
                
            elseif idx > 1 && idx < scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                     
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                    end
                end
              
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                    
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*columnOut.cumLHR(idx11,idx);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
   
                
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            dummyProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            eqCOMDupireSpotGF.localVolSurface.volProxy= ones(size(dummyProxy))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           initProb = zeros(1,gridSize);
           initProb(idxDummyS) = 1.0-weight;
           initProb(idxDummyS-1) = weight;
           
           initPriceC = zeros(length(Ks),1);
           initPriceP = zeros(length(Ks),1);
            
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           for idxh=1:length(Ks)
               initPriceC(idxh) = max(S0-Ks(idxh),0.0);
               initPriceP(idxh) = max(-S0+Ks(idxh),0.0);
           end
           
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           nextProb = initProb;
           nextPriceC = initPriceC;
           nextPriceP = initPriceP;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),...
%                                 nextXIdx,nextXWeight,nextProb,nextPriceC,nextPriceP,U(:,idx));
                            
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                            
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             

        
        function out = computeStepdown1SMCMCINT(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
%                                 nextXIdx,nextXWeight,U(:,idx));
                            
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
%                     nextXIdxRef = mcmcOut.nextXIdxRef;
%                     nextXWeightRef = mcmcOut.nextXWeightRef;
                    
%                     periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
%                 if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                     columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
%                 else
%                     columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
%                 end
                
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
%                 cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
%                             %LHR measure change onto original
%                             contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
%                             unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
%            cumLHR_avg = mean(columnOut.cumLHR);
%            out.cumLHR_last = cumLHR_avg(end);
           
        end
        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
                            
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                else
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                end
                
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                            %LHR measure change onto original
                            contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                            unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
           cumLHR_avg = mean(columnOut.cumLHR);
           out.cumLHR_last = cumLHR_avg(end);
           
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx+1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx+1);
           
           out.hitValue = hitValue; 
           if stepdownParams.params('KIYN') == true
                out.unhitValue = hitValue;
           else
               out.unhitValue = unhitValue;
           end
           
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1);
           
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           cumulativeLikelyHoodRatio = ones(modelStatesSize,1);
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           %% likelyHoodRatio Calc
           for i=1:modelStatesSize
                payoffStateA.cashflow(i) = payoffStateA.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateB.cashflow(i) = payoffStateB.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateC.cashflow(i) =  payoffStateC.cashflow(i)*cumulativeLikelyHoodRatio(i);
           end
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            fwdPriceC = params.lastPriceC;
            fwdPRiceP = params.lastPriceP;
            
            optParams.params = params;
            optParams.params.GFType = -1;
            optParams.params.volProxyRefYN = 'NO';
            optParams.params.oneStepDt = 1.0/365.0;
            optParams.Ks = params.Ks;
            optParams.dK = params.dK;
            optParams.ipos = params.ipos;
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            optParams.idxNow = idxNow;
            %relevent volProxy
            volProxy   = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            
            dTDays = 0;
            
            if idxNow~=1
                fromTime = expiry(idxNow-1);
                toTime = maturity;
            else % idxNow == 1
                fromTime = 0;
                toTime = maturity;
                
            end
            
%             proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            outForward = BootStrapGFForward(eqCOMDupireSpotGF,volProxy,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams);
            
            cValue = outForward.fwdPriceCOut;
            pValue = outForward.fwdPricePOut;
            
            settleFutures = eqCOMDupireSpotGF.settleFutures;
            forward = settleFutures(idxNow);
            
            strikeSize = length(strikes);
            
            out.impVol = zeros(1,strikeSize);
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.impVol(i) = blackVolLBR(marKetPrice,forward,K, maturity/365.0,-1);
                else
                     marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                     out.impVol(i) = blackVolLBR(marKetPrice,forward,K, maturity/365.0,1);
                end
            end
            
            
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,targetExpiry,targetStrikes)
            
            params.expiry        = eqCOMDupireSpotGF.localVolSurface.expiry;
            params.pricingIdx    = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            params.pricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
            params.Ks            = eqCOMDupireSpotGF.localVolSurface.Ks;
            params.Ns = length(params.Ks); 
            params.dK = params.Ks(2) - params.Ks(1);
            
            targetStrikesPerExpirySize = size(targetStrikes,2);
           
            
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            
            if strcmp(eqCOMDupireSpotGF.modelParams('useSettleFuturesYN'),'YES')
                S0 = eqCOMDupireSpotGF.settleFutures(1);
            else
                S0 = eqCOMDupireSpotGF.FwdNM(0);
            end
            
%             S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            lastPriceC = initPriceC;
            lastPriceP = initPriceP;
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                for idx=1:targetStrikesPerExpirySize
                    params.ipos(idx) = floor( (strikePerExpiry(idx) - params.Ks(1))/params.dK) + 1;  % add default 1
                    params.iweight(idx) = (strikePerExpiry(idx) - params.Ks(params.ipos(idx)))/params.dK;
                end
                
                params.lastPriceC = lastPriceC;
                params.lastPriceP = lastPriceP;
                
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                
                lastPriceC = outDummy.cValue;
                lastPriceP = outDummy.pValue;
                
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
%                     probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
%             out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
           fwdPriceC = optParams.lastPriceC;
           fwdPriceP = optParams.lastPriceP;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdPriceC,fwdPriceP,optParams);
           
           fwdPriceCNew = out.fwdPriceCOut;
           fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,optParams); 
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
               marketImpVol = optParams.params.blackVolRef;
           else
               marketImpVol = optParams.params.blackVol;
           end
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
                blackOTMPrices = optParams.params.blackOTMPricesRef;
           else
               blackOTMPrices = optParams.params.blackOTMPrices;
           end
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastPriceC,lastPriceP,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastPriceC = lastPriceC;
            optParams.lastPriceP = lastPriceP;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            if strcmp(params.volProxyRefYN,'YES')
                for i=1:params.strikeSize
                    tvar(i) = params.blackVolRef(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
            else
                for i=1:params.strikeSize
                    tvar(i) = params.blackVol(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
                
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            % Added 20190214 by sungwoo hong
            dummyOut = targetfunc(x);
            bootStrapOut.modelImpVolPost = dummyOut.modelImpVol;
            
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastPriceC,lastPriceP,optParams);
            
            bootStrapOut.lastPriceC = out.fwdPriceCOut;
            bootStrapOut.lastPriceP = out.fwdPricePOut;
            
        end
        
        
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            volSurfaceRef = black.volSurfaceRef;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackVolRef = zeros(expirySize,strikeSize);
            
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            
            blackOTMPricesRef = zeros(expirySize,strikeSize);
            fwdMoneynessRef = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end
            
            if  strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVolRef(k,j) = volSurfaceRef.volSurfaceR(k,j);
                        fwdMoneynessRef(k,j) = strike(j)/fwd;
                        marketStrikesRef(k,j) = strike(j);
                        
                        if fwdMoneynessRef(k,j) <= 1.0
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'P');
                        else
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'C');
                        end
                        
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.volSurfaceRef = volSurfaceRef;
            
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackOTMPricesRef = blackOTMPricesRef;
            
            params.blackVol = blackVol;
            
            params.blackVolRef = blackVolRef;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            params.fwdMoneynessRef = fwdMoneynessRef;
            
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            if strcmp(eqCOMDupireSpotGF.modelParams('useSettleFuturesYN'),'YES')
                S0 = eqCOMDupireSpotGF.settleFutures(1);
            else
                S0 = eqCOMDupireSpotGF.FwdNM(0);
            end
            
            idxDummy = find(S0 >= params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = max(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (S0 - params.Ks(idxDummyS))/params.dK;

              %% Ref Curve update
            if strcmp(eqCOMDupireSpotGF.modelParams('useSettleFuturesYN'),'YES')
                S0Ref = eqCOMDupireSpotGF.settleFuturesRef(1);
            else
                S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            end
            
            idxDummyRef = find(S0Ref >= params.Ks);
            if isempty(idxDummyRef)
                error('S0Ref is not covered in the grid K')
            end

            idxDummySRef = max(idxDummyRef);
            params.PricingidxRef = idxDummySRef;
            params.PricingWeightRef = (S0Ref - params.Ks(idxDummySRef))/params.dK;
            
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            params.volProxyRefYN = eqCOMDupireSpotGF.modelParams('volProxyRefYN');
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            
            out.fwdMoneynessRef = fwdMoneynessRef;
            
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyRef = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR') ...
                    || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            if strcmp(eqCOMDupireSpotGF.modelParams('useSettleFuturesYN'),'YES')
                S0 = eqCOMDupireSpotGF.settleFutures(1);
            else
                S0 = eqCOMDupireSpotGF.FwdNM(0);
            end
            
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            initPriceCRef = zeros(params.Ns,1);
            initPricePRef = zeros(params.Ns,1);
            
            if strcmp(eqCOMDupireSpotGF.modelParams('useSettleFuturesYN'),'YES')
                S0Ref = eqCOMDupireSpotGF.settleFuturesRef(1);
            else
                S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            end
            
            for idxh=1:params.Ns
                initPriceCRef(idxh) = max(S0Ref-params.Ks(idxh),0.0);
                initPricePRef(idxh) = max(-S0Ref+params.Ks(idxh),0.0);
            end
            
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPricesRef = blackOTMPricesRef;
            
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.blackVolRef =blackVolRef;
            
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.modelImpVolRef  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.interpBlackPricesRef = zeros(expirySize,strikeSize);
            out.dupireOTMPricesRef = zeros(expirySize,strikeSize);
            out.dupireBlackVolRef = zeros(expirySize,strikeSize);
            out.volErrorRef = zeros(expirySize,strikeSize);
            out.priceReRef = zeros(expirySize,strikeSize);
            out.priceReOrigRef = zeros(expirySize,strikeSize);
            out.marketStrikesRef = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.PricingidxRef = params.PricingidxRef;
            out.PricingWeightRef = params.PricingWeightRef;
            out.nIterRef = zeros(expirySize,1);
            out.localVolRef = zeros(expirySize,length(out.Ks));
            out.rmseTotalRef=0.0;
            out.fwdVolMseTotalRef = 0.0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
            case 'bootstrapLikely'
                    
                %% calibrate to reference forward Curve start
%                    
                    %vol proxy calibration
                    

                    
                    if strcmp(params.volProxyRefYN,'YES')

                        lastPriceCRef = initPriceCRef;
                        lastPricePRef = initPricePRef;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceCRef,lastPricePRef,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrigRef(i,j) = bootStrapOut.volProxy(j);
                                out.volProxyRef(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.iposRef(i,j)     = bootStrapOut.ipos(j);
                                out.volErrorRef(i,j) = bootStrapOut.volError(j);
                                out.marketImpVolRef(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVolRef(i,j) =  bootStrapOut.modelImpVol(j);
                                out.modelImpVolRefPost(i,j) =  bootStrapOut.modelImpVolPost(j);
                                out.interpBlackPricesRef(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPricesRef(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceReRef(i,j) = out.dupireOTMPricesRef(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrigRef(i,j) = out.dupireOTMPricesRef(i,j)/out.blackOTMPricesRef(i,j)-1.0;
                                out.marketStrikesRef(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIterRef(i) = bootStrapOut.nIter;
                            tempLocalVolRef = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVolRef(i,j) = tempLocalVolRef(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceCRef = bootStrapOut.lastPriceC;
                            lastPricePRef = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotalRef = out.rmseTotalRef + out.priceReOrigRef(j,k)*out.priceReOrigRef(j,k);
                                    out.fwdVolMseTotalRef = out.fwdVolMseTotalRef + out.volErrorRef(j,k)*out.volErrorRef(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotalRef = sqrt(out.rmseTotalRef/N);
                        out.fwdVolMseTotalRef = sqrt(out.fwdVolMseTotalRef/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxyRef = out.volProxyRef;
                        eqCOMDupireSpotGF.localVolSurface.iposRef = out.iposRef;
                        eqCOMDupireSpotGF.localVolSurface.localVolRef = out.localVolRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingidxRef = out.PricingidxRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeightRef = out.PricingWeightRef;

                        %% calibrate to spot forward curve end
                    
                    else
                     %% calibrate to spot forward curve start

                        lastPriceC = initPriceC;
                        lastPriceP = initPriceP;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                                out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.ipos(i,j)     = bootStrapOut.ipos(j);
                                out.volError(i,j) = bootStrapOut.volError(j);
                                out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                                out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIter(i) = bootStrapOut.nIter;
                            tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVol(i,j) = tempLocalVol(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceC = bootStrapOut.lastPriceC;
                            lastPriceP = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                    out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                        eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                        eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                        eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
    
                        eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                        eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                        eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                        eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;

                        eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;

                      %% calibrate to spot forward curve end   
                    end
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMFLSimpleProbGridCS < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        %Likely
        settleFuturesRef
        
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMFLSimpleProbGridCS(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            for i=1:length(Ks)
                localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
            end   
                
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdProb,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           if strcmp(optParams.params.volProxyRefYN,'YES') 
               refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           else
               refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           end
           
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
               
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           KsSize = length(Ks);
           dK = optParams.dK;
%            priceC = fwdPriceC;
%            priceP = fwdPRiceP;
           
           
           prob = fwdProb;
           condProb = eye(KsSize,KsSize);
           
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        prob,optParams);

%                priceC = outGF.newProb;
%                priceP = outGF.newPriceP;
               
               prob = outGF.newProb;
               
%                condProb = condProb*outGF.condProb;
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
%                    dummyC = priceC;
%                    dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   exDividendTransProb = zeros(KsSize,KsSize);
                   
                   for  i = 1:KsSize
                       dummyX = Ks(i)*(1.0 + dividendRatio);
                       idxDummy = find(dummyX < Ks);
                       if isempty(idxDummy)
                           idxDummyS = length(Ks);
                           weight = 0.0;
                       else
                           idxDummyS = min(idxDummy);
                           if idxDummyS == 1
                               weight = 0.0;
                           else
                               weight = (Ks(idxDummyS) - dummyX)/dK;
                           end
                       end

                       if idxDummyS == 1
                           exDividendTransProb(i,1) = 1.0;
                       else
                           exDividendTransProb(i,idxDummyS) = 1.0 -weight;
                           exDividendTransProb(i,idxDummyS-1) = weight;
                       end
                   end
                   
                   prob = prob * exDividendTransProb;
               end
           end
           
%            out.fwdPriceCOut = condProb * priceC;
%            out.fwdPricePOut = condProb * priceP;
           
           out.fwdProbOut = prob;
           out.condProb = condProb;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,prob,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(prob),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(prob);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newProb = prob*A_exp1;
                condProb = A_exp1;
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   KsSize = length(Ks);
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   % construct exDividendTransProb
                   exDividendTransProb = zeros(KsSize,KsSize);
                   for  i = 1:KsSize
                       dummyX = Ks(i)*(1.0 + dividendRatio);
                       idxDummy = find(dummyX < Ks);
                       if isempty(idxDummy)
                           idxDummyS = length(Ks);
                           weight = 0.0;
                       else
                           idxDummyS = min(idxDummy);
                           if idxDummyS == 1
                               weight = 0.0;
                           else
                               weight = (Ks(idxDummyS) - dummyX)/dK;
                           end
                       end

                       if idxDummyS == 1
                           exDividendTransProb(i,1) = 1.0;
                       else
                           exDividendTransProb(i,idxDummyS) = 1.0 -weight;
                           exDividendTransProb(i,idxDummyS-1) = weight;
                       end
                   end
                   
                   % multiply exDividendTransProb to the inducted payoff
                   lastPrice = exDividendTransProb * lastPrice;
                   
%                    for  idxzz= 1:length(dummyC)
%                        NGP = floor( (Ks(idxzz)*(1.0 + dividendRatio) - Ks(1))/dK) + 1;
%                        if NGP < 1
%                            NGP = 1;
%                        end
%                        
%                        if NGP > length(dummyC)-1
%                            NGP = length(dummyC)-1;
%                        end
%                        
%                        weight = (Ks(idxzz)*(1.0 + dividendRatio)-Ks(NGP))/dK;
%                        lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
%                        
%                        if lastPrice(idxzz) < 0
%                             lastPrice(idxzz) = 0.0;
%                        end
%                    end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYNFlag);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1),volProxyRefYN);
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            if strcmp(volProxyRefYNFlag,'YES')
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxyRef(idxNow,:);
            else
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            end
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            
            for ii =1:length(x)
                localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
            end
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            KsSize = length(Ks);
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            %% modify probDist
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
                currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               exDividendTransProb = zeros(KsSize,KsSize);
               exDividendTransProbRef = zeros(KsSize,KsSize);
               
               %% exDividendTransProb
               for i=1:KsSize
                   dummyX = Ks(i)*(1.0 + dividendRatio);
                   idxDummy = find(dummyX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - dummyX)/dK;
                       end
                   end
                   
                   if idxDummyS == 1
                       exDividendTransProb(i,1) = 1.0;
                   else
                       exDividendTransProb(i,idxDummyS) = 1.0 -weight;
                       exDividendTransProb(i,idxDummyS-1) = weight;
                   end
               end
               
               %% adjust condProb to reflect discreteDividend Jump
               condProb = condProb * exDividendTransProb;
               %% exDividendTransProbRef
               for i=1:KsSize
                   dummyXRef = Ks(i)*(1.0 + dividendRatioRef);
                   idxDummyRef = find(dummyXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - dummyXRef)/dK;
                       end
                   end
                   
                   if idxDummySRef == 1
                       exDividendTransProbRef(i,1) = 1.0;
                   else
                       exDividendTransProbRef(i,idxDummySRef) = 1.0 -weightRef;
                       exDividendTransProbRef(i,idxDummySRef-1) = weightRef;
                   end
               end
               
                %% adjust condProb to reflect discreteDividend Jump
               condProbRef = condProbRef * exDividendTransProbRef;
                
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
           
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardLikely(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
            
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
%            %% renormalize Radon Nikodym Derivatives 
%             if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                 avgLHR = mean(likelyHoodRatio);
%                 likelyHoodRatio = likelyHoodRatio/avgLHR;
%             end
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
            %% importtant correction above
            
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   
                 %% dividendRatioRef start
                   if nextXIdxRef(i) ==1 
                       nextXRef = Ks(nextXIdxRef(i));
                   else
                       nextXRef = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextXRef = nextXRef*(1.0 + dividendRatioRef);
                   idxDummyRef = find(nextXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - nextXRef)/dK;
                       end
                   end

                   out.nextXIdxRef(i) = idxDummySRef;
                   out.nextXWeightRef(i) = weightRef;
                 
                 %% dividendRatioRef end
                 
                   if nextXIdxRef(i) ==1 
                       nextX = Ks(nextXIdxRef(i));
                   else
                       nextX = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == length(Ks) || idxH1 == 0
                    nextXWeight(i) = 0.0;
                else
                    upperZ = norminv(cumProb(idxH1));
                    lowerZ = norminv(cumProb(idxH1-1));
                    sampleZ = norminv(uSample(i));
                    nextXWeight(i) = (upperZ -sampleZ)/(upperZ-lowerZ);
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyP)
                       predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdProbNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            if strcmp(params.params.volProxyRefYN,'YES')
                settleFutures = eqCOMDupireSpotGF.settleFuturesRef;
            else
                settleFutures = eqCOMDupireSpotGF.settleFutures;
            end
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
%             cValue = fwdPriceCNew;
%             pValue = fwdPricePNew;

            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = fwdProbNew * meshC;
            pValue = fwdProbNew * meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
%                      marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1);
                     marKetPrice = pValue(i);
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1);
                    marKetPrice = cValue(i); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffLikely(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
            cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
            if idx ~= 1 
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                        cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    end
                end
              
                
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*cumulativeLikelyHoodRatio(idx11);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
                
            end    
            
            
        end
      
        function columnOut = MCPayoffLikelyRen(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
           %% sum(cumLHR2) = N - sum(cumLHR1); 
            cumulativeLikelyHoodRatio = zeros(modelStatesSize,1);
            
            dumMeasureSum = 0.0;
            dumMeasureSumPrev = 0.0;
            dumMeasureN = 0;
            if idx == 1 
                cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
                dumMeasureSum = sum(cumulativeLikelyHoodRatio);
                cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/dumMeasureSum*modelStatesSize;
                columnOut.cumLHR(:,idx) = cumulativeLikelyHoodRatio;
            else
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % dead path
                        dumMeasureSumPrev = dumMeasureSumPrev + columnIn.cumLHR(idx11,idx-1);
                        dumMeasureN = dumMeasureN + 1;
                    end
                end
                
                if dumMeasureN < modelStatesSize % if alive path normalize the relative measure
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                            dumMeasureSum = dumMeasureSum + cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                    
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = cumulativeLikelyHoodRatio(idx11)/(dumMeasureSum)*(modelStatesSize - dumMeasureSumPrev);
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                
                for idx11 =1:modelStatesSize % 1st early redemption
                        % every path is an alive path use all path to
                       
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                end
                
                
            elseif idx > 1 && idx < scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                     
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                    end
                end
              
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                    
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*columnOut.cumLHR(idx11,idx);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
   
                
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            eqCOMDupireSpotGF.localVolSurface.volProxy = ones(size(fwdMoneyness))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           initProb = zeros(1,gridSize);
           initProb(idxDummyS) = 1.0-weight;
           initProb(idxDummyS-1) = weight;
           
           initPriceC = zeros(length(Ks),1);
           initPriceP = zeros(length(Ks),1);
            
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           for idxh=1:length(Ks)
               initPriceC(idxh) = max(S0-Ks(idxh),0.0);
               initPriceP(idxh) = max(-S0+Ks(idxh),0.0);
           end
           
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           nextProb = initProb;
           nextPriceC = initPriceC;
           nextPriceP = initPriceP;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),...
%                                 nextXIdx,nextXWeight,nextProb,nextPriceC,nextPriceP,U(:,idx));
                            
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                            
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             

        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
%                                 nextXIdx,nextXWeight,U(:,idx));
                            
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
                            
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                else
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                end
                
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                            %LHR measure change onto original
                            contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                            unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
           cumLHR_avg = mean(columnOut.cumLHR);
           out.cumLHR_last = cumLHR_avg(end);
           
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx-1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx-1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx-1);
           
           out.hitValue = hitValue; 
           
           KIYN = stepdownParams.params('KIYN');
           
           if KIYN == true
                out.unhitValue = hitValue;
           else
               out.unhitValue = unhitValue;
           end
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1);
           
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           cumulativeLikelyHoodRatio = ones(modelStatesSize,1);
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           %% likelyHoodRatio Calc
           for i=1:modelStatesSize
                payoffStateA.cashflow(i) = payoffStateA.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateB.cashflow(i) = payoffStateB.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateC.cashflow(i) =  payoffStateC.cashflow(i)*cumulativeLikelyHoodRatio(i);
           end
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
%            fwdPriceC = optParams.lastPriceC;
%            fwdPriceP = optParams.lastPriceP;
           
           fwdProb = optParams.lastProb;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdProb,optParams);
           
           fwdProbNew = out.fwdProbOut;
%            fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdProbNew,optParams); 
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
               marketImpVol = optParams.params.blackVolRef;
           else
               marketImpVol = optParams.params.blackVol;
           end
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
                blackOTMPrices = optParams.params.blackOTMPricesRef;
           else
               blackOTMPrices = optParams.params.blackOTMPrices;
           end
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastProb,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
%             optParams.lastPriceC = lastPriceC;
%             optParams.lastPriceP = lastPriceP;
            
            optParams.lastProb = lastProb;
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            if strcmp(params.volProxyRefYN,'YES')
                for i=1:params.strikeSize
                    tvar(i) = params.blackVolRef(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
            else
                for i=1:params.strikeSize
                    tvar(i) = params.blackVol(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
                
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastProb,optParams);
            
            bootStrapOut.lastProb = out.fwdProbOut;
            
        end
        
        
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            volSurfaceRef = black.volSurfaceRef;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackVolRef = zeros(expirySize,strikeSize);
            
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            
            blackOTMPricesRef = zeros(expirySize,strikeSize);
            fwdMoneynessRef = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end
            
            if  strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVolRef(k,j) = volSurfaceRef.volSurfaceR(k,j);
                        fwdMoneynessRef(k,j) = strike(j)/fwd;
                        marketStrikesRef(k,j) = strike(j);
                        
                        if fwdMoneynessRef(k,j) <= 1.0
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'P');
                        else
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'C');
                        end
                        
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.volSurfaceRef = volSurfaceRef;
            
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackOTMPricesRef = blackOTMPricesRef;
            
            params.blackVol = blackVol;
            
            params.blackVolRef = blackVolRef;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            params.fwdMoneynessRef = fwdMoneynessRef;
            
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            idxDummy = find(S0 < params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end
            
            idxDummyS = min(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (params.Ks(idxDummyS) - S0)/params.dK;
            
          %% Ref Curve update
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            
            idxDummyRef = find(S0Ref < params.Ks);
            if isempty(idxDummyRef)
                error('S0Ref is not covered in the grid K')
            end
            
            idxDummySRef = min(idxDummyRef);
            params.PricingidxRef = idxDummySRef;
            params.PricingWeightRef = (params.Ks(idxDummySRef)- S0Ref)/params.dK;
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            
            out.fwdMoneynessRef = fwdMoneynessRef;
            
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyRef = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR') ...
                    || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            initProb = zeros(1,params.Ns);
            if params.Pricingidx == 1
                initProb(1) = 1.0;
            else
                initProb(params.Pricingidx) = 1.0 -params.PricingWeight;
                initProb(params.Pricingidx-1) = params.PricingWeight;
            end
            
            initProbRef = zeros(1,params.Ns);
            if params.PricingidxRef == 1
                initProbRef(1) = 1.0;
            else
                initProbRef(params.PricingidxRef) = 1.0 -params.PricingWeightRef;
                initProbRef(params.PricingidxRef-1) = params.PricingWeightRef;
            end
            
%             initPriceC = zeros(params.Ns,1);
%             initPriceP = zeros(params.Ns,1);
            
%             S0 = eqCOMDupireSpotGF.FwdNM(0);
%             for idxh=1:params.Ns
%                 initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
%                 initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
%             end
%             
%             initPriceCRef = zeros(params.Ns,1);
%             initPricePRef = zeros(params.Ns,1);
%             
%             S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
%             for idxh=1:params.Ns
%                 initPriceCRef(idxh) = max(S0Ref-params.Ks(idxh),0.0);
%                 initPricePRef(idxh) = max(-S0Ref+params.Ks(idxh),0.0);
%             end
%             
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPricesRef = blackOTMPricesRef;
            
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.blackVolRef =blackVolRef;
            
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.modelImpVolRef  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.interpBlackPricesRef = zeros(expirySize,strikeSize);
            out.dupireOTMPricesRef = zeros(expirySize,strikeSize);
            out.dupireBlackVolRef = zeros(expirySize,strikeSize);
            out.volErrorRef = zeros(expirySize,strikeSize);
            out.priceReRef = zeros(expirySize,strikeSize);
            out.priceReOrigRef = zeros(expirySize,strikeSize);
            out.marketStrikesRef = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.PricingidxRef = params.PricingidxRef;
            out.PricingWeightRef = params.PricingWeightRef;
            out.nIterRef = zeros(expirySize,1);
            out.localVolRef = zeros(expirySize,length(out.Ks));
            out.rmseTotalRef=0.0;
            out.fwdVolMseTotalRef = 0.0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
            case 'bootstrapLikely'
                    
                %% calibrate to reference forward Curve start
%                    
                    %vol proxy calibration
                    
                    params.volProxyRefYN = eqCOMDupireSpotGF.modelParams('volProxyRefYN');
                    
                    if strcmp(params.volProxyRefYN,'YES')

%                         lastPriceCRef = initPriceCRef;
%                         lastPricePRef = initPricePRef;
                        
                        lastProb = initProbRef;
%                         latProb = initProb;
                        
                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastProb,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrigRef(i,j) = bootStrapOut.volProxy(j);
                                out.volProxyRef(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.iposRef(i,j)     = bootStrapOut.ipos(j);
                                out.volErrorRef(i,j) = bootStrapOut.volError(j);
                                out.marketImpVolRef(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVolRef(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPricesRef(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPricesRef(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceReRef(i,j) = out.dupireOTMPricesRef(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrigRef(i,j) = out.dupireOTMPricesRef(i,j)/out.blackOTMPricesRef(i,j)-1.0;
                                out.marketStrikesRef(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIterRef(i) = bootStrapOut.nIter;
                            tempLocalVolRef = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVolRef(i,j) = tempLocalVolRef(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
%                             lastPriceCRef = bootStrapOut.lastPriceC;
%                             lastPricePRef = bootStrapOut.lastPriceP;
                            
                            lastProb = bootStrapOut.lastProb;
                            
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotalRef = out.rmseTotalRef + out.priceReOrigRef(j,k)*out.priceReOrigRef(j,k);
                                    out.fwdVolMseTotalRef = out.fwdVolMseTotalRef + out.volErrorRef(j,k)*out.volErrorRef(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotalRef = sqrt(out.rmseTotalRef/N);
                        out.fwdVolMseTotalRef = sqrt(out.fwdVolMseTotalRef/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxyRef = out.volProxyRef;
                        eqCOMDupireSpotGF.localVolSurface.iposRef = out.iposRef;
                        eqCOMDupireSpotGF.localVolSurface.localVolRef = out.localVolRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingidxRef = out.PricingidxRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeightRef = out.PricingWeightRef;

                        %% calibrate to spot forward curve end
                    
                    else
                     %% calibrate to spot forward curve start

%                         lastPriceC = initPriceC;
%                         lastPriceP = initPriceP;
                        
                        latProb = initProb;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,latProb,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                                out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.ipos(i,j)     = bootStrapOut.ipos(j);
                                out.volError(i,j) = bootStrapOut.volError(j);
                                out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                                out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIter(i) = bootStrapOut.nIter;
                            tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVol(i,j) = tempLocalVol(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
%                             lastPriceC = bootStrapOut.lastPriceC;
%                             lastPriceP = bootStrapOut.lastPriceP;
                            
                            latProb = bootStrapOut.lastProb;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                    out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                        eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                        eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                        eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
    
                        eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                        eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                        eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                        eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;

                        eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;

                      %% calibrate to spot forward curve end   
                    end
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMFLSimpleProbGrid < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        %Likely
        settleFuturesRef
        
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMFLSimpleProbGrid(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='Linear';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'linear')
                localVol = interp1(volProxyKs,volProxy,Ks);
            else
                localVol = pchip(volProxyKs,volProxy,Ks);
            end
%             for i=1:length(Ks)
%                 localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),3);
%             end   
                
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdProb,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           if strcmp(optParams.params.volProxyRefYN,'YES') 
               refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           else
               refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           end
           
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
               
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           KsSize = length(Ks);
           dK = optParams.dK;
%            priceC = fwdPriceC;
%            priceP = fwdPRiceP;
           
           
           prob = fwdProb;
           condProb = eye(KsSize,KsSize);
           
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        prob,optParams);

%                priceC = outGF.newProb;
%                priceP = outGF.newPriceP;
               
               prob = outGF.newProb;
               
%                condProb = condProb*outGF.condProb;
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
%                    dummyC = priceC;
%                    dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   exDividendTransProb = zeros(KsSize,KsSize);
                   
                   for  i = 1:KsSize
                       dummyX = Ks(i)*(1.0 + dividendRatio);
                       idxDummy = find(dummyX < Ks);
                       if isempty(idxDummy)
                           idxDummyS = length(Ks);
                           weight = 0.0;
                       else
                           idxDummyS = min(idxDummy);
                           if idxDummyS == 1
                               weight = 0.0;
                           else
                               weight = (Ks(idxDummyS) - dummyX)/dK;
                           end
                       end

                       if idxDummyS == 1
                           exDividendTransProb(i,1) = 1.0;
                       else
                           exDividendTransProb(i,idxDummyS) = 1.0 -weight;
                           exDividendTransProb(i,idxDummyS-1) = weight;
                       end
                   end
                   
                   prob = prob * exDividendTransProb;
               end
           end
           
%            out.fwdPriceCOut = condProb * priceC;
%            out.fwdPricePOut = condProb * priceP;
           
           out.fwdProbOut = prob;
           out.condProb = condProb;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,prob,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(prob),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(prob);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newProb = prob*A_exp1;
                condProb = A_exp1;
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   KsSize = length(Ks);
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   % construct exDividendTransProb
                   exDividendTransProb = zeros(KsSize,KsSize);
                   for  i = 1:KsSize
                       dummyX = Ks(i)*(1.0 + dividendRatio);
                       idxDummy = find(dummyX < Ks);
                       if isempty(idxDummy)
                           idxDummyS = length(Ks);
                           weight = 0.0;
                       else
                           idxDummyS = min(idxDummy);
                           if idxDummyS == 1
                               weight = 0.0;
                           else
                               weight = (Ks(idxDummyS) - dummyX)/dK;
                           end
                       end

                       if idxDummyS == 1
                           exDividendTransProb(i,1) = 1.0;
                       else
                           exDividendTransProb(i,idxDummyS) = 1.0 -weight;
                           exDividendTransProb(i,idxDummyS-1) = weight;
                       end
                   end
                   
                   % multiply exDividendTransProb to the inducted payoff
                   lastPrice = exDividendTransProb * lastPrice;
                   
%                    for  idxzz= 1:length(dummyC)
%                        NGP = floor( (Ks(idxzz)*(1.0 + dividendRatio) - Ks(1))/dK) + 1;
%                        if NGP < 1
%                            NGP = 1;
%                        end
%                        
%                        if NGP > length(dummyC)-1
%                            NGP = length(dummyC)-1;
%                        end
%                        
%                        weight = (Ks(idxzz)*(1.0 + dividendRatio)-Ks(NGP))/dK;
%                        lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
%                        
%                        if lastPrice(idxzz) < 0
%                             lastPrice(idxzz) = 0.0;
%                        end
%                    end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYNFlag);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1),volProxyRefYN);
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            if strcmp(volProxyRefYNFlag,'YES')
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxyRef(idxNow,:);
            else
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            end
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
%             localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
%             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
%             localVol =  zeros(length(x),1);
%             for ii =1:length(x)
%                 localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
%             end
            
            volProxy  =  eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            volProxyKs = eqCOMDupireSpotGF.marketStrikes(idxNow,:);
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'linear')
                localVol = interp1(volProxyKs,volProxy,x);
            else
                localVol = pchip(volProxyKs,volProxy,x);
            end
            %             Ks = params.Ks;
            
            
           
            
            
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            KsSize = length(Ks);
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            %% modify probDist
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
                currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               exDividendTransProb = zeros(KsSize,KsSize);
               exDividendTransProbRef = zeros(KsSize,KsSize);
               
               %% exDividendTransProb
               for i=1:KsSize
                   dummyX = Ks(i)*(1.0 + dividendRatio);
                   idxDummy = find(dummyX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - dummyX)/dK;
                       end
                   end
                   
                   if idxDummyS == 1
                       exDividendTransProb(i,1) = 1.0;
                   else
                       exDividendTransProb(i,idxDummyS) = 1.0 -weight;
                       exDividendTransProb(i,idxDummyS-1) = weight;
                   end
               end
               
               %% adjust condProb to reflect discreteDividend Jump
               condProb = condProb * exDividendTransProb;
               %% exDividendTransProbRef
               for i=1:KsSize
                   dummyXRef = Ks(i)*(1.0 + dividendRatioRef);
                   idxDummyRef = find(dummyXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - dummyXRef)/dK;
                       end
                   end
                   
                   if idxDummySRef == 1
                       exDividendTransProbRef(i,1) = 1.0;
                   else
                       exDividendTransProbRef(i,idxDummySRef) = 1.0 -weightRef;
                       exDividendTransProbRef(i,idxDummySRef-1) = weightRef;
                   end
               end
               
                %% adjust condProb to reflect discreteDividend Jump
               condProbRef = condProbRef * exDividendTransProbRef;
                
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
           
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardLikely(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
            
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
%            %% renormalize Radon Nikodym Derivatives 
%             if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                 avgLHR = mean(likelyHoodRatio);
%                 likelyHoodRatio = likelyHoodRatio/avgLHR;
%             end
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
            %% importtant correction above
            
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   
                 %% dividendRatioRef start
                   if nextXIdxRef(i) ==1 
                       nextXRef = Ks(nextXIdxRef(i));
                   else
                       nextXRef = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextXRef = nextXRef*(1.0 + dividendRatioRef);
                   idxDummyRef = find(nextXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - nextXRef)/dK;
                       end
                   end

                   out.nextXIdxRef(i) = idxDummySRef;
                   out.nextXWeightRef(i) = weightRef;
                 
                 %% dividendRatioRef end
                 
                   if nextXIdxRef(i) ==1 
                       nextX = Ks(nextXIdxRef(i));
                   else
                       nextX = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == length(Ks) || idxH1 == 0
                    nextXWeight(i) = 0.0;
                else
                    upperZ = norminv(cumProb(idxH1));
                    lowerZ = norminv(cumProb(idxH1-1));
                    sampleZ = norminv(uSample(i));
                    nextXWeight(i) = (upperZ -sampleZ)/(upperZ-lowerZ);
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyP)
                       predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdProbNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            if strcmp(params.params.volProxyRefYN,'YES')
                settleFutures = eqCOMDupireSpotGF.settleFuturesRef;
            else
                settleFutures = eqCOMDupireSpotGF.settleFutures;
            end
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
%             cValue = fwdPriceCNew;
%             pValue = fwdPricePNew;

            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = fwdProbNew * meshC;
            pValue = fwdProbNew * meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
%                      marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1);
                     marKetPrice = pValue(i);
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1);
                    marKetPrice = cValue(i); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffLikely(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
            cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
            if idx ~= 1 
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                        cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    end
                end
              
                
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*cumulativeLikelyHoodRatio(idx11);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
                
            end    
            
            
        end
      
        function columnOut = MCPayoffLikelyRen(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
           %% sum(cumLHR2) = N - sum(cumLHR1); 
            cumulativeLikelyHoodRatio = zeros(modelStatesSize,1);
            
            dumMeasureSum = 0.0;
            dumMeasureSumPrev = 0.0;
            dumMeasureN = 0;
            if idx == 1 
                cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
                dumMeasureSum = sum(cumulativeLikelyHoodRatio);
                cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/dumMeasureSum*modelStatesSize;
                columnOut.cumLHR(:,idx) = cumulativeLikelyHoodRatio;
            else
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % dead path
                        dumMeasureSumPrev = dumMeasureSumPrev + columnIn.cumLHR(idx11,idx-1);
                        dumMeasureN = dumMeasureN + 1;
                    end
                end
                
                if dumMeasureN < modelStatesSize % if alive path normalize the relative measure
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                            dumMeasureSum = dumMeasureSum + cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                    
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = cumulativeLikelyHoodRatio(idx11)/(dumMeasureSum)*(modelStatesSize - dumMeasureSumPrev);
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                
                for idx11 =1:modelStatesSize % 1st early redemption
                        % every path is an alive path use all path to
                       
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                end
                
                
            elseif idx > 1 && idx < scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                     
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                    end
                end
              
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                    
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*columnOut.cumLHR(idx11,idx);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
   
                
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            eqCOMDupireSpotGF.localVolSurface.volProxy = ones(size(fwdMoneyness))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           initProb = zeros(1,gridSize);
           initProb(idxDummyS) = 1.0-weight;
           initProb(idxDummyS-1) = weight;
           
           initPriceC = zeros(length(Ks),1);
           initPriceP = zeros(length(Ks),1);
            
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           for idxh=1:length(Ks)
               initPriceC(idxh) = max(S0-Ks(idxh),0.0);
               initPriceP(idxh) = max(-S0+Ks(idxh),0.0);
           end
           
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           nextProb = initProb;
           nextPriceC = initPriceC;
           nextPriceP = initPriceP;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),...
%                                 nextXIdx,nextXWeight,nextProb,nextPriceC,nextPriceP,U(:,idx));
                            
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                            
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             

        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
%                                 nextXIdx,nextXWeight,U(:,idx));
                            
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
                            
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                else
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                end
                
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                            %LHR measure change onto original
                            contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                            unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
           cumLHR_avg = mean(columnOut.cumLHR);
           out.cumLHR_last = cumLHR_avg(end);
           
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx-1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx-1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx-1);
           
           out.hitValue = hitValue; 
           
           KIYN = stepdownParams.params('KIYN');
           
           if KIYN == true
                out.unhitValue = hitValue;
           else
               out.unhitValue = unhitValue;
           end
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1);
           
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           cumulativeLikelyHoodRatio = ones(modelStatesSize,1);
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           %% likelyHoodRatio Calc
           for i=1:modelStatesSize
                payoffStateA.cashflow(i) = payoffStateA.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateB.cashflow(i) = payoffStateB.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateC.cashflow(i) =  payoffStateC.cashflow(i)*cumulativeLikelyHoodRatio(i);
           end
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
%            fwdPriceC = optParams.lastPriceC;
%            fwdPriceP = optParams.lastPriceP;
           
           fwdProb = optParams.lastProb;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdProb,optParams);
           
           fwdProbNew = out.fwdProbOut;
%            fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdProbNew,optParams); 
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
               marketImpVol = optParams.params.blackVolRef;
           else
               marketImpVol = optParams.params.blackVol;
           end
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
                blackOTMPrices = optParams.params.blackOTMPricesRef;
           else
               blackOTMPrices = optParams.params.blackOTMPrices;
           end
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastProb,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
%             optParams.lastPriceC = lastPriceC;
%             optParams.lastPriceP = lastPriceP;
            
            optParams.lastProb = lastProb;
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            if strcmp(params.volProxyRefYN,'YES')
                for i=1:params.strikeSize
                    tvar(i) = params.blackVolRef(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
            else
                for i=1:params.strikeSize
                    tvar(i) = params.blackVol(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
                
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastProb,optParams);
            
            bootStrapOut.lastProb = out.fwdProbOut;
            
        end
        
        
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            volSurfaceRef = black.volSurfaceRef;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackVolRef = zeros(expirySize,strikeSize);
            
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            
            blackOTMPricesRef = zeros(expirySize,strikeSize);
            fwdMoneynessRef = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end
            
            if  strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVolRef(k,j) = volSurfaceRef.volSurfaceR(k,j);
                        fwdMoneynessRef(k,j) = strike(j)/fwd;
                        marketStrikesRef(k,j) = strike(j);
                        
                        if fwdMoneynessRef(k,j) <= 1.0
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'P');
                        else
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'C');
                        end
                        
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.volSurfaceRef = volSurfaceRef;
            
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackOTMPricesRef = blackOTMPricesRef;
            
            params.blackVol = blackVol;
            
            params.blackVolRef = blackVolRef;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            params.fwdMoneynessRef = fwdMoneynessRef;
            
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            idxDummy = find(S0 < params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end
            
            idxDummyS = min(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (params.Ks(idxDummyS) - S0)/params.dK;
            
          %% Ref Curve update
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            
            idxDummyRef = find(S0Ref < params.Ks);
            if isempty(idxDummyRef)
                error('S0Ref is not covered in the grid K')
            end
            
            idxDummySRef = min(idxDummyRef);
            params.PricingidxRef = idxDummySRef;
            params.PricingWeightRef = (params.Ks(idxDummySRef)- S0Ref)/params.dK;
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            
            out.fwdMoneynessRef = fwdMoneynessRef;
            
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyRef = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR') ...
                    || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            initProb = zeros(1,params.Ns);
            if params.Pricingidx == 1
                initProb(1) = 1.0;
            else
                initProb(params.Pricingidx) = 1.0 -params.PricingWeight;
                initProb(params.Pricingidx-1) = params.PricingWeight;
            end
            
            initProbRef = zeros(1,params.Ns);
            if params.PricingidxRef == 1
                initProbRef(1) = 1.0;
            else
                initProbRef(params.PricingidxRef) = 1.0 -params.PricingWeightRef;
                initProbRef(params.PricingidxRef-1) = params.PricingWeightRef;
            end
            
%             initPriceC = zeros(params.Ns,1);
%             initPriceP = zeros(params.Ns,1);
            
%             S0 = eqCOMDupireSpotGF.FwdNM(0);
%             for idxh=1:params.Ns
%                 initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
%                 initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
%             end
%             
%             initPriceCRef = zeros(params.Ns,1);
%             initPricePRef = zeros(params.Ns,1);
%             
%             S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
%             for idxh=1:params.Ns
%                 initPriceCRef(idxh) = max(S0Ref-params.Ks(idxh),0.0);
%                 initPricePRef(idxh) = max(-S0Ref+params.Ks(idxh),0.0);
%             end
%             
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPricesRef = blackOTMPricesRef;
            
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.blackVolRef =blackVolRef;
            
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.modelImpVolRef  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.interpBlackPricesRef = zeros(expirySize,strikeSize);
            out.dupireOTMPricesRef = zeros(expirySize,strikeSize);
            out.dupireBlackVolRef = zeros(expirySize,strikeSize);
            out.volErrorRef = zeros(expirySize,strikeSize);
            out.priceReRef = zeros(expirySize,strikeSize);
            out.priceReOrigRef = zeros(expirySize,strikeSize);
            out.marketStrikesRef = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.PricingidxRef = params.PricingidxRef;
            out.PricingWeightRef = params.PricingWeightRef;
            out.nIterRef = zeros(expirySize,1);
            out.localVolRef = zeros(expirySize,length(out.Ks));
            out.rmseTotalRef=0.0;
            out.fwdVolMseTotalRef = 0.0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
            case 'bootstrapLikely'
                    
                %% calibrate to reference forward Curve start
%                    
                    %vol proxy calibration
                    
                    params.volProxyRefYN = eqCOMDupireSpotGF.modelParams('volProxyRefYN');
                    
                    if strcmp(params.volProxyRefYN,'YES')

%                         lastPriceCRef = initPriceCRef;
%                         lastPricePRef = initPricePRef;
                        
                        lastProb = initProbRef;
%                         latProb = initProb;
                        
                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastProb,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrigRef(i,j) = bootStrapOut.volProxy(j);
                                out.volProxyRef(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.iposRef(i,j)     = bootStrapOut.ipos(j);
                                out.volErrorRef(i,j) = bootStrapOut.volError(j);
                                out.marketImpVolRef(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVolRef(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPricesRef(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPricesRef(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceReRef(i,j) = out.dupireOTMPricesRef(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrigRef(i,j) = out.dupireOTMPricesRef(i,j)/out.blackOTMPricesRef(i,j)-1.0;
                                out.marketStrikesRef(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIterRef(i) = bootStrapOut.nIter;
                            tempLocalVolRef = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVolRef(i,j) = tempLocalVolRef(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
%                             lastPriceCRef = bootStrapOut.lastPriceC;
%                             lastPricePRef = bootStrapOut.lastPriceP;
                            
                            lastProb = bootStrapOut.lastProb;
                            
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotalRef = out.rmseTotalRef + out.priceReOrigRef(j,k)*out.priceReOrigRef(j,k);
                                    out.fwdVolMseTotalRef = out.fwdVolMseTotalRef + out.volErrorRef(j,k)*out.volErrorRef(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotalRef = sqrt(out.rmseTotalRef/N);
                        out.fwdVolMseTotalRef = sqrt(out.fwdVolMseTotalRef/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxyRef = out.volProxyRef;
                        eqCOMDupireSpotGF.localVolSurface.iposRef = out.iposRef;
                        eqCOMDupireSpotGF.localVolSurface.localVolRef = out.localVolRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingidxRef = out.PricingidxRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeightRef = out.PricingWeightRef;

                        %% calibrate to spot forward curve end
                    
                    else
                     %% calibrate to spot forward curve start

%                         lastPriceC = initPriceC;
%                         lastPriceP = initPriceP;
                        
                        latProb = initProb;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,latProb,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                                out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.ipos(i,j)     = bootStrapOut.ipos(j);
                                out.volError(i,j) = bootStrapOut.volError(j);
                                out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                                out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIter(i) = bootStrapOut.nIter;
                            tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVol(i,j) = tempLocalVol(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
%                             lastPriceC = bootStrapOut.lastPriceC;
%                             lastPriceP = bootStrapOut.lastPriceP;
                            
                            latProb = bootStrapOut.lastProb;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                    out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                        eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                        eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                        eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
    
                        eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                        eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                        eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                        eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;

                        eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;

                      %% calibrate to spot forward curve end   
                    end
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMFLSimpleProbCons < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        %Likely
        settleFuturesRef
        
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMFLSimpleProbCons(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            for i=1:length(Ks)
                localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
            end   
                
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           if strcmp(optParams.params.volProxyRefYN,'YES') 
               refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           else
               refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           end
           
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
               
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           dK = optParams.dK;
           priceC = fwdPriceC;
           priceP = fwdPRiceP;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        priceC,priceP,optParams);

               priceC = outGF.newPriceC;
               priceP = outGF.newPriceP;
               
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = priceC;
                   dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                       priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                       priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                       priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);
                       
                       if priceC(idxzz) < 0
                            priceC(idxzz) = 0.0;
                       end
                       
                       if priceP(idxzz) < 0
                           priceP(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           out.fwdPriceCOut = priceC;
           out.fwdPricePOut = priceP;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,priceC,priceP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(priceC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(priceC);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newPriceC = A_exp1*priceC;
                newPriceP = A_exp1*priceP;
            
            end
            
            out.newPriceC = newPriceC;
            out.newPriceP = newPriceP;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)*(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)*(1.0 + dividendRatio)-Ks(NGP))/dK;
                       lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       
                       if lastPrice(idxzz) < 0
                            lastPrice(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYNFlag);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1),volProxyRefYN);
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            if strcmp(volProxyRefYNFlag,'YES')
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxyRef(idxNow,:);
            else
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            end
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            
            for ii =1:length(x)
                localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
            end
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            KsSize = length(Ks);
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            %% modify probDist
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
                currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               exDividendTransProb = zeros(KsSize,KsSize);
               exDividendTransProbRef = zeros(KsSize,KsSize);
               
               %% exDividendTransProb
               for i=1:KsSize
                   dummyX = Ks(i)*(1.0 + dividendRatio);
                   idxDummy = find(dummyX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - dummyX)/dK;
                       end
                   end
                   
                   if idxDummyS == 1
                       exDividendTransProb(i,1) = 1.0;
                   else
                       exDividendTransProb(i,idxDummyS) = 1.0 -weight;
                       exDividendTransProb(i,idxDummyS-1) = weight;
                   end
               end
               
               %% adjust condProb to reflect discreteDividend Jump
               condProb = condProb * exDividendTransProb;
               %% exDividendTransProbRef
               for i=1:KsSize
                   dummyXRef = Ks(i)*(1.0 + dividendRatioRef);
                   idxDummyRef = find(dummyXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - dummyXRef)/dK;
                       end
                   end
                   
                   if idxDummySRef == 1
                       exDividendTransProbRef(i,1) = 1.0;
                   else
                       exDividendTransProbRef(i,idxDummySRef) = 1.0 -weightRef;
                       exDividendTransProbRef(i,idxDummySRef-1) = weightRef;
                   end
               end
               
                %% adjust condProb to reflect discreteDividend Jump
               condProbRef = condProbRef * exDividendTransProbRef;
                
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
           
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardLikely(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
            
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
%            %% renormalize Radon Nikodym Derivatives 
%             if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                 avgLHR = mean(likelyHoodRatio);
%                 likelyHoodRatio = likelyHoodRatio/avgLHR;
%             end
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
            %% importtant correction above
            
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   
                 %% dividendRatioRef start
                   if nextXIdxRef(i) ==1 
                       nextXRef = Ks(nextXIdxRef(i));
                   else
                       nextXRef = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextXRef = nextXRef*(1.0 + dividendRatioRef);
                   idxDummyRef = find(nextXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - nextXRef)/dK;
                       end
                   end

                   out.nextXIdxRef(i) = idxDummySRef;
                   out.nextXWeightRef(i) = weightRef;
                 
                 %% dividendRatioRef end
                 
                   if nextXIdxRef(i) ==1 
                       nextX = Ks(nextXIdxRef(i));
                   else
                       nextX = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == length(Ks) || idxH1 == 0
                    nextXWeight(i) = 0.0;
                else
                    upperZ = norminv(cumProb(idxH1));
                    lowerZ = norminv(cumProb(idxH1-1));
                    sampleZ = norminv(uSample(i));
                    nextXWeight(i) = (upperZ -sampleZ)/(upperZ-lowerZ);
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyP)
                       predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            if strcmp(params.params.volProxyRefYN,'YES')
                settleFutures = eqCOMDupireSpotGF.settleFuturesRef;
            else
                settleFutures = eqCOMDupireSpotGF.settleFutures;
            end
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            cValue = fwdPriceCNew;
            pValue = fwdPricePNew;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffLikely(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
            cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
            if idx ~= 1 
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                        cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    end
                end
              
                
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*cumulativeLikelyHoodRatio(idx11);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
                
            end    
            
            
        end
      
        function columnOut = MCPayoffLikelyRen(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
           %% sum(cumLHR2) = N - sum(cumLHR1); 
            cumulativeLikelyHoodRatio = zeros(modelStatesSize,1);
            
            dumMeasureSum = 0.0;
            dumMeasureSumPrev = 0.0;
            dumMeasureN = 0;
            if idx == 1 
                cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
                dumMeasureSum = sum(cumulativeLikelyHoodRatio);
                cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/dumMeasureSum*modelStatesSize;
                columnOut.cumLHR(:,idx) = cumulativeLikelyHoodRatio;
            else
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % dead path
                        dumMeasureSumPrev = dumMeasureSumPrev + columnIn.cumLHR(idx11,idx-1);
                        dumMeasureN = dumMeasureN + 1;
                    end
                end
                
                if dumMeasureN < modelStatesSize % if alive path normalize the relative measure
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                            dumMeasureSum = dumMeasureSum + cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                    
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = cumulativeLikelyHoodRatio(idx11)/(dumMeasureSum)*(modelStatesSize - dumMeasureSumPrev);
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                
                for idx11 =1:modelStatesSize % 1st early redemption
                        % every path is an alive path use all path to
                       
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                end
                
                
            elseif idx > 1 && idx < scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                     
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                    end
                end
              
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                    
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*columnOut.cumLHR(idx11,idx);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
   
                
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            eqCOMDupireSpotGF.localVolSurface.volProxy = ones(size(fwdMoneyness))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           initProb = zeros(1,gridSize);
           initProb(idxDummyS) = 1.0-weight;
           initProb(idxDummyS-1) = weight;
           
           initPriceC = zeros(length(Ks),1);
           initPriceP = zeros(length(Ks),1);
            
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           for idxh=1:length(Ks)
               initPriceC(idxh) = max(S0-Ks(idxh),0.0);
               initPriceP(idxh) = max(-S0+Ks(idxh),0.0);
           end
           
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           nextProb = initProb;
           nextPriceC = initPriceC;
           nextPriceP = initPriceP;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),...
%                                 nextXIdx,nextXWeight,nextProb,nextPriceC,nextPriceP,U(:,idx));
                            
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                            
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             

        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
                            
%                     mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
%                                 nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                else
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                end
                
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                            %LHR measure change onto original
                            contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                            unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
           cumLHR_avg = mean(columnOut.cumLHR);
           out.cumLHR_last = cumLHR_avg(end);
           
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx+1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx+1);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1);
           
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           cumulativeLikelyHoodRatio = ones(modelStatesSize,1);
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           %% likelyHoodRatio Calc
           for i=1:modelStatesSize
                payoffStateA.cashflow(i) = payoffStateA.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateB.cashflow(i) = payoffStateB.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateC.cashflow(i) =  payoffStateC.cashflow(i)*cumulativeLikelyHoodRatio(i);
           end
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
           fwdPriceC = optParams.lastPriceC;
           fwdPriceP = optParams.lastPriceP;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdPriceC,fwdPriceP,optParams);
           
           fwdPriceCNew = out.fwdPriceCOut;
           fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,optParams); 
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
               marketImpVol = optParams.params.blackVolRef;
           else
               marketImpVol = optParams.params.blackVol;
           end
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
                blackOTMPrices = optParams.params.blackOTMPricesRef;
           else
               blackOTMPrices = optParams.params.blackOTMPrices;
           end
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastPriceC,lastPriceP,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastPriceC = lastPriceC;
            optParams.lastPriceP = lastPriceP;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            if strcmp(params.volProxyRefYN,'YES')
                for i=1:params.strikeSize
                    tvar(i) = params.blackVolRef(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
            else
                for i=1:params.strikeSize
                    tvar(i) = params.blackVol(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
                
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastPriceC,lastPriceP,optParams);
            
            bootStrapOut.lastPriceC = out.fwdPriceCOut;
            bootStrapOut.lastPriceP = out.fwdPricePOut;
            
        end
        
        
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            volSurfaceRef = black.volSurfaceRef;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackVolRef = zeros(expirySize,strikeSize);
            
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            
            blackOTMPricesRef = zeros(expirySize,strikeSize);
            fwdMoneynessRef = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end
            
            if  strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVolRef(k,j) = volSurfaceRef.volSurfaceR(k,j);
                        fwdMoneynessRef(k,j) = strike(j)/fwd;
                        marketStrikesRef(k,j) = strike(j);
                        
                        if fwdMoneynessRef(k,j) <= 1.0
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'P');
                        else
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'C');
                        end
                        
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.volSurfaceRef = volSurfaceRef;
            
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackOTMPricesRef = blackOTMPricesRef;
            
            params.blackVol = blackVol;
            
            params.blackVolRef = blackVolRef;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            params.fwdMoneynessRef = fwdMoneynessRef;
            
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            idxDummy = find(S0 >= params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end
            
            idxDummyS = max(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (S0 - params.Ks(idxDummyS))/params.dK;
            
          %% Ref Curve update
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            
            idxDummyRef = find(S0Ref >= params.Ks);
            if isempty(idxDummyRef)
                error('S0Ref is not covered in the grid K')
            end
            
            idxDummySRef = max(idxDummyRef);
            params.PricingidxRef = idxDummySRef;
            params.PricingWeightRef = (S0Ref - params.Ks(idxDummySRef))/params.dK;
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            
            out.fwdMoneynessRef = fwdMoneynessRef;
            
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyRef = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR') ...
                    || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            initPriceCRef = zeros(params.Ns,1);
            initPricePRef = zeros(params.Ns,1);
            
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            for idxh=1:params.Ns
                initPriceCRef(idxh) = max(S0Ref-params.Ks(idxh),0.0);
                initPricePRef(idxh) = max(-S0Ref+params.Ks(idxh),0.0);
            end
            
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPricesRef = blackOTMPricesRef;
            
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.blackVolRef =blackVolRef;
            
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.modelImpVolRef  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.interpBlackPricesRef = zeros(expirySize,strikeSize);
            out.dupireOTMPricesRef = zeros(expirySize,strikeSize);
            out.dupireBlackVolRef = zeros(expirySize,strikeSize);
            out.volErrorRef = zeros(expirySize,strikeSize);
            out.priceReRef = zeros(expirySize,strikeSize);
            out.priceReOrigRef = zeros(expirySize,strikeSize);
            out.marketStrikesRef = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.PricingidxRef = params.PricingidxRef;
            out.PricingWeightRef = params.PricingWeightRef;
            out.nIterRef = zeros(expirySize,1);
            out.localVolRef = zeros(expirySize,length(out.Ks));
            out.rmseTotalRef=0.0;
            out.fwdVolMseTotalRef = 0.0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
            case 'bootstrapLikely'
                    
                %% calibrate to reference forward Curve start
%                    
                    %vol proxy calibration
                    
                    params.volProxyRefYN = eqCOMDupireSpotGF.modelParams('volProxyRefYN');
                    
                    if strcmp(params.volProxyRefYN,'YES')

                        lastPriceCRef = initPriceCRef;
                        lastPricePRef = initPricePRef;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceCRef,lastPricePRef,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrigRef(i,j) = bootStrapOut.volProxy(j);
                                out.volProxyRef(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.iposRef(i,j)     = bootStrapOut.ipos(j);
                                out.volErrorRef(i,j) = bootStrapOut.volError(j);
                                out.marketImpVolRef(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVolRef(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPricesRef(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPricesRef(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceReRef(i,j) = out.dupireOTMPricesRef(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrigRef(i,j) = out.dupireOTMPricesRef(i,j)/out.blackOTMPricesRef(i,j)-1.0;
                                out.marketStrikesRef(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIterRef(i) = bootStrapOut.nIter;
                            tempLocalVolRef = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVolRef(i,j) = tempLocalVolRef(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceCRef = bootStrapOut.lastPriceC;
                            lastPricePRef = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotalRef = out.rmseTotalRef + out.priceReOrigRef(j,k)*out.priceReOrigRef(j,k);
                                    out.fwdVolMseTotalRef = out.fwdVolMseTotalRef + out.volErrorRef(j,k)*out.volErrorRef(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotalRef = sqrt(out.rmseTotalRef/N);
                        out.fwdVolMseTotalRef = sqrt(out.fwdVolMseTotalRef/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxyRef = out.volProxyRef;
                        eqCOMDupireSpotGF.localVolSurface.iposRef = out.iposRef;
                        eqCOMDupireSpotGF.localVolSurface.localVolRef = out.localVolRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingidxRef = out.PricingidxRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeightRef = out.PricingWeightRef;

                        %% calibrate to spot forward curve end
                    
                    else
                     %% calibrate to spot forward curve start

                        lastPriceC = initPriceC;
                        lastPriceP = initPriceP;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                                out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.ipos(i,j)     = bootStrapOut.ipos(j);
                                out.volError(i,j) = bootStrapOut.volError(j);
                                out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                                out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIter(i) = bootStrapOut.nIter;
                            tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVol(i,j) = tempLocalVol(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceC = bootStrapOut.lastPriceC;
                            lastPriceP = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                    out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                        eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                        eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                        eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
    
                        eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                        eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                        eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                        eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;

                        eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;

                      %% calibrate to spot forward curve end   
                    end
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMFLSimpleProb < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        %Likely
        settleFuturesRef
        
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMFLSimpleProb(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            for i=1:length(Ks)
                localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
            end   
                
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           if strcmp(optParams.params.volProxyRefYN,'YES') 
               refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           else
               refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           end
           
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
               
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           dK = optParams.dK;
           priceC = fwdPriceC;
           priceP = fwdPRiceP;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        priceC,priceP,optParams);

               priceC = outGF.newPriceC;
               priceP = outGF.newPriceP;
               
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = priceC;
                   dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                       priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                       priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                       priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);
                       
                       if priceC(idxzz) < 0
                            priceC(idxzz) = 0.0;
                       end
                       
                       if priceP(idxzz) < 0
                           priceP(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           out.fwdPriceCOut = priceC;
           out.fwdPricePOut = priceP;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,priceC,priceP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(priceC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(priceC);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newPriceC = A_exp1*priceC;
                newPriceP = A_exp1*priceP;
            
            end
            
            out.newPriceC = newPriceC;
            out.newPriceP = newPriceP;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)*(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)*(1.0 + dividendRatio)-Ks(NGP))/dK;
                       lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       
                       if lastPrice(idxzz) < 0
                            lastPrice(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYNFlag);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1),volProxyRefYN);
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            if strcmp(volProxyRefYNFlag,'YES')
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxyRef(idxNow,:);
            else
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            end
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            
            for ii =1:length(x)
                localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
            end
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            KsSize = length(Ks);
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            %% modify probDist
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
                currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               exDividendTransProb = zeros(KsSize,KsSize);
               exDividendTransProbRef = zeros(KsSize,KsSize);
               
               %% exDividendTransProb
               for i=1:KsSize
                   dummyX = Ks(i)*(1.0 + dividendRatio);
                   idxDummy = find(dummyX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - dummyX)/dK;
                       end
                   end
                   
                   if idxDummyS == 1
                       exDividendTransProb(i,1) = 1.0;
                   else
                       exDividendTransProb(i,idxDummyS) = 1.0 -weight;
                       exDividendTransProb(i,idxDummyS-1) = weight;
                   end
               end
               
               %% adjust condProb to reflect discreteDividend Jump
               condProb = condProb * exDividendTransProb;
               %% exDividendTransProbRef
               for i=1:KsSize
                   dummyXRef = Ks(i)*(1.0 + dividendRatioRef);
                   idxDummyRef = find(dummyXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - dummyXRef)/dK;
                       end
                   end
                   
                   if idxDummySRef == 1
                       exDividendTransProbRef(i,1) = 1.0;
                   else
                       exDividendTransProbRef(i,idxDummySRef) = 1.0 -weightRef;
                       exDividendTransProbRef(i,idxDummySRef-1) = weightRef;
                   end
               end
               
                %% adjust condProb to reflect discreteDividend Jump
               condProbRef = condProbRef * exDividendTransProbRef;
                
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
           
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardLikely(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
            
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
%            %% renormalize Radon Nikodym Derivatives 
%             if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                 avgLHR = mean(likelyHoodRatio);
%                 likelyHoodRatio = likelyHoodRatio/avgLHR;
%             end
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
            %% importtant correction above
            
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   
                 %% dividendRatioRef start
                   if nextXIdxRef(i) ==1 
                       nextXRef = Ks(nextXIdxRef(i));
                   else
                       nextXRef = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextXRef = nextXRef*(1.0 + dividendRatioRef);
                   idxDummyRef = find(nextXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - nextXRef)/dK;
                       end
                   end

                   out.nextXIdxRef(i) = idxDummySRef;
                   out.nextXWeightRef(i) = weightRef;
                 
                 %% dividendRatioRef end
                 
                   if nextXIdxRef(i) ==1 
                       nextX = Ks(nextXIdxRef(i));
                   else
                       nextX = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == length(Ks) || idxH1 == 0
                    nextXWeight(i) = 0.0;
                else
                    upperZ = norminv(cumProb(idxH1));
                    lowerZ = norminv(cumProb(idxH1-1));
                    sampleZ = norminv(uSample(i));
                    nextXWeight(i) = (upperZ -sampleZ)/(upperZ-lowerZ);
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyP)
                       predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            if strcmp(params.params.volProxyRefYN,'YES')
                settleFutures = eqCOMDupireSpotGF.settleFuturesRef;
            else
                settleFutures = eqCOMDupireSpotGF.settleFutures;
            end
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            cValue = fwdPriceCNew;
            pValue = fwdPricePNew;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffLikely(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
            cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
            if idx ~= 1 
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                        cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    end
                end
              
                
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*cumulativeLikelyHoodRatio(idx11);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
                
            end    
            
            
        end
      
        function columnOut = MCPayoffLikelyRen(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
           %% sum(cumLHR2) = N - sum(cumLHR1); 
            cumulativeLikelyHoodRatio = zeros(modelStatesSize,1);
            
            dumMeasureSum = 0.0;
            dumMeasureSumPrev = 0.0;
            dumMeasureN = 0;
            if idx == 1 
                cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
                dumMeasureSum = sum(cumulativeLikelyHoodRatio);
                cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/dumMeasureSum*modelStatesSize;
                columnOut.cumLHR(:,idx) = cumulativeLikelyHoodRatio;
            else
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % dead path
                        dumMeasureSumPrev = dumMeasureSumPrev + columnIn.cumLHR(idx11,idx-1);
                        dumMeasureN = dumMeasureN + 1;
                    end
                end
                
                if dumMeasureN < modelStatesSize % if alive path normalize the relative measure
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                            dumMeasureSum = dumMeasureSum + cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                    
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = cumulativeLikelyHoodRatio(idx11)/(dumMeasureSum)*(modelStatesSize - dumMeasureSumPrev);
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                
                for idx11 =1:modelStatesSize % 1st early redemption
                        % every path is an alive path use all path to
                       
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                end
                
                
            elseif idx > 1 && idx < scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                     
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                    end
                end
              
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                    
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*columnOut.cumLHR(idx11,idx);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
   
                
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            eqCOMDupireSpotGF.localVolSurface.volProxy = ones(size(fwdMoneyness))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           initProb = zeros(1,gridSize);
           initProb(idxDummyS) = 1.0-weight;
           initProb(idxDummyS-1) = weight;
           
           initPriceC = zeros(length(Ks),1);
           initPriceP = zeros(length(Ks),1);
            
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           for idxh=1:length(Ks)
               initPriceC(idxh) = max(S0-Ks(idxh),0.0);
               initPriceP(idxh) = max(-S0+Ks(idxh),0.0);
           end
           
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           nextProb = initProb;
           nextPriceC = initPriceC;
           nextPriceP = initPriceP;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),...
%                                 nextXIdx,nextXWeight,nextProb,nextPriceC,nextPriceP,U(:,idx));
                            
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                            
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             

        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
                            
%                     mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
%                                 nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                else
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                end
                
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                            %LHR measure change onto original
                            contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                            unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
           cumLHR_avg = mean(columnOut.cumLHR);
           out.cumLHR_last = cumLHR_avg(end);
           
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx+1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx+1);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1);
           
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           cumulativeLikelyHoodRatio = ones(modelStatesSize,1);
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           %% likelyHoodRatio Calc
           for i=1:modelStatesSize
                payoffStateA.cashflow(i) = payoffStateA.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateB.cashflow(i) = payoffStateB.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateC.cashflow(i) =  payoffStateC.cashflow(i)*cumulativeLikelyHoodRatio(i);
           end
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
           fwdPriceC = optParams.lastPriceC;
           fwdPriceP = optParams.lastPriceP;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdPriceC,fwdPriceP,optParams);
           
           fwdPriceCNew = out.fwdPriceCOut;
           fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,optParams); 
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
               marketImpVol = optParams.params.blackVolRef;
           else
               marketImpVol = optParams.params.blackVol;
           end
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
                blackOTMPrices = optParams.params.blackOTMPricesRef;
           else
               blackOTMPrices = optParams.params.blackOTMPrices;
           end
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastPriceC,lastPriceP,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastPriceC = lastPriceC;
            optParams.lastPriceP = lastPriceP;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            if strcmp(params.volProxyRefYN,'YES')
                for i=1:params.strikeSize
                    tvar(i) = params.blackVolRef(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
            else
                for i=1:params.strikeSize
                    tvar(i) = params.blackVol(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
                
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastPriceC,lastPriceP,optParams);
            
            bootStrapOut.lastPriceC = out.fwdPriceCOut;
            bootStrapOut.lastPriceP = out.fwdPricePOut;
            
        end
        
        
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            volSurfaceRef = black.volSurfaceRef;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackVolRef = zeros(expirySize,strikeSize);
            
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            
            blackOTMPricesRef = zeros(expirySize,strikeSize);
            fwdMoneynessRef = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end
            
            if  strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVolRef(k,j) = volSurfaceRef.volSurfaceR(k,j);
                        fwdMoneynessRef(k,j) = strike(j)/fwd;
                        marketStrikesRef(k,j) = strike(j);
                        
                        if fwdMoneynessRef(k,j) <= 1.0
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'P');
                        else
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'C');
                        end
                        
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.volSurfaceRef = volSurfaceRef;
            
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackOTMPricesRef = blackOTMPricesRef;
            
            params.blackVol = blackVol;
            
            params.blackVolRef = blackVolRef;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            params.fwdMoneynessRef = fwdMoneynessRef;
            
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            idxDummy = find(S0 >= params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end
            
            idxDummyS = max(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (S0 - params.Ks(idxDummyS))/params.dK;
            
          %% Ref Curve update
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            
            idxDummyRef = find(S0Ref >= params.Ks);
            if isempty(idxDummyRef)
                error('S0Ref is not covered in the grid K')
            end
            
            idxDummySRef = max(idxDummyRef);
            params.PricingidxRef = idxDummySRef;
            params.PricingWeightRef = (S0Ref - params.Ks(idxDummySRef))/params.dK;
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            
            out.fwdMoneynessRef = fwdMoneynessRef;
            
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyRef = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR') ...
                    || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            initPriceCRef = zeros(params.Ns,1);
            initPricePRef = zeros(params.Ns,1);
            
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            for idxh=1:params.Ns
                initPriceCRef(idxh) = max(S0Ref-params.Ks(idxh),0.0);
                initPricePRef(idxh) = max(-S0Ref+params.Ks(idxh),0.0);
            end
            
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPricesRef = blackOTMPricesRef;
            
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.blackVolRef =blackVolRef;
            
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.modelImpVolRef  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.interpBlackPricesRef = zeros(expirySize,strikeSize);
            out.dupireOTMPricesRef = zeros(expirySize,strikeSize);
            out.dupireBlackVolRef = zeros(expirySize,strikeSize);
            out.volErrorRef = zeros(expirySize,strikeSize);
            out.priceReRef = zeros(expirySize,strikeSize);
            out.priceReOrigRef = zeros(expirySize,strikeSize);
            out.marketStrikesRef = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.PricingidxRef = params.PricingidxRef;
            out.PricingWeightRef = params.PricingWeightRef;
            out.nIterRef = zeros(expirySize,1);
            out.localVolRef = zeros(expirySize,length(out.Ks));
            out.rmseTotalRef=0.0;
            out.fwdVolMseTotalRef = 0.0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
            case 'bootstrapLikely'
                    
                %% calibrate to reference forward Curve start
%                    
                    %vol proxy calibration
                    
                    params.volProxyRefYN = eqCOMDupireSpotGF.modelParams('volProxyRefYN');
                    
                    if strcmp(params.volProxyRefYN,'YES')

                        lastPriceCRef = initPriceCRef;
                        lastPricePRef = initPricePRef;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceCRef,lastPricePRef,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrigRef(i,j) = bootStrapOut.volProxy(j);
                                out.volProxyRef(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.iposRef(i,j)     = bootStrapOut.ipos(j);
                                out.volErrorRef(i,j) = bootStrapOut.volError(j);
                                out.marketImpVolRef(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVolRef(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPricesRef(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPricesRef(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceReRef(i,j) = out.dupireOTMPricesRef(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrigRef(i,j) = out.dupireOTMPricesRef(i,j)/out.blackOTMPricesRef(i,j)-1.0;
                                out.marketStrikesRef(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIterRef(i) = bootStrapOut.nIter;
                            tempLocalVolRef = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVolRef(i,j) = tempLocalVolRef(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceCRef = bootStrapOut.lastPriceC;
                            lastPricePRef = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotalRef = out.rmseTotalRef + out.priceReOrigRef(j,k)*out.priceReOrigRef(j,k);
                                    out.fwdVolMseTotalRef = out.fwdVolMseTotalRef + out.volErrorRef(j,k)*out.volErrorRef(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotalRef = sqrt(out.rmseTotalRef/N);
                        out.fwdVolMseTotalRef = sqrt(out.fwdVolMseTotalRef/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxyRef = out.volProxyRef;
                        eqCOMDupireSpotGF.localVolSurface.iposRef = out.iposRef;
                        eqCOMDupireSpotGF.localVolSurface.localVolRef = out.localVolRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingidxRef = out.PricingidxRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeightRef = out.PricingWeightRef;

                        %% calibrate to spot forward curve end
                    
                    else
                     %% calibrate to spot forward curve start

                        lastPriceC = initPriceC;
                        lastPriceP = initPriceP;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                                out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.ipos(i,j)     = bootStrapOut.ipos(j);
                                out.volError(i,j) = bootStrapOut.volError(j);
                                out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                                out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIter(i) = bootStrapOut.nIter;
                            tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVol(i,j) = tempLocalVol(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceC = bootStrapOut.lastPriceC;
                            lastPriceP = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                    out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                        eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                        eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                        eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
    
                        eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                        eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                        eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                        eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;

                        eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;

                      %% calibrate to spot forward curve end   
                    end
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMFLSimpleAmount < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        %Likely
        settleFuturesRef
        
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMFLSimpleAmount(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            localVol = interp1(volProxyKs,volProxy,Ks','linear','extrap');
            
%             for i=1:length(Ks)
%                 localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
%             end   
                
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           if strcmp(optParams.params.volProxyRefYN,'YES') 
               refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           else
               refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           end
           
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
               
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           dK = optParams.dK;
           priceC = fwdPriceC;
           priceP = fwdPRiceP;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        priceC,priceP,optParams);

               priceC = outGF.newPriceC;
               priceP = outGF.newPriceP;
               
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = priceC;
                   dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   
%                    dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   dividendAmount = refFuturesValue(nextFuturesIdx) - refFuturesValue(currentFuturesIdx);
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz) - dividendAmount - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = ((Ks(idxzz) - dividendAmount)-Ks(NGP))/dK;
                       priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       
                       priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                       
                       if priceC(idxzz) < 0
                            priceC(idxzz) = 0.0;
                       end
                       
                       if priceP(idxzz) < 0
                           priceP(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           out.fwdPriceCOut = priceC;
           out.fwdPricePOut = priceP;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,priceC,priceP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(priceC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(priceC);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newPriceC = A_exp1*priceC;
                newPriceP = A_exp1*priceP;
            
            end
            
            out.newPriceC = newPriceC;
            out.newPriceP = newPriceP;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
%                    dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   dividendAmount = refFuturesValue(nextFuturesIdx) - refFuturesValue(currentFuturesIdx);
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz) + dividendAmount - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz) + dividendAmount -Ks(NGP))/dK;
                       lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       
                       if lastPrice(idxzz) < 0
                            lastPrice(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYNFlag);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1),volProxyRefYN);
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            if strcmp(volProxyRefYNFlag,'YES')
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxyRef(idxNow,:);
            else
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            end
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            
            volProxy   = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            volProxyKs = eqCOMDupireSpotGF.localVolSurface.marketStrikes(idxNow,:);
            
            localVol = interp1(volProxyKs,volProxy,x','linear','extrap');
            
            
%             localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
%             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
%             
            
%             for ii =1:length(x)
%                 localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
%             end
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,...
                        lastProb,lastPriceC, lastPriceP,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            
            nextProb = lastProb*condProb;
            nextPriceC = condProb*lastPriceC;
            % Check the ex-dividend date & if it is then adjust prob accordingly 
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               dummyProb = nextProb;
               dummyC = nextPriceC; 
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;

               if dividendRatio > 0
                   
               end
               for  idxzz= 1:length(dummyProb)
                   NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                   if NGP < 1
                       NGP = 1;
                   end

                   if NGP > length(dummyC)-1
                       NGP = length(dummyC)-1;
                   end

                   weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                   priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                   priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                   priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                   priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);

                   if priceC(idxzz) < 0
                        priceC(idxzz) = 0.0;
                   end

                   if priceP(idxzz) < 0
                       priceP(idxzz) = 0.0;
                   end

               end
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalCumPerExpiry(nextProb,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nPoints = length(Ks);
            
            debugDx = zeros(NMC,1);
            debugIdx1 = zeros(NMC,1);
            debugIdx2 = zeros(NMC,1);
            debugWeight1 = zeros(NMC,1);
            debugWeight2 = zeros(NMC,1);
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                
                idxH1 = min(find(uSample(i) < cumProb1));
                idxH2 = min(find(uSample(i) < cumProb2));
                debugDx(i) = idxH1-idxH2;
                debugIdx1(i) = idxH1;
                debugIdx2(i) = idxH2;
                
                nextX = (1.0-lastXWeight(i))*Ks(idxH1) + lastXWeight(i)*Ks(idxH2);
                idxDummy = find(nextX < Ks);
                if isempty(idxDummy)
                    error('nextX is not covered in the grid K')
                end
                
                idxDummyS = min(idxDummy);
                weight = (Ks(idxDummyS)-nextX)/dK;
                nextXIdx(i) = idxDummyS;
                nextXWeight(i) = weight;
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;

            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
%                dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               dividendAmount = refFuturesValue(nextFuturesIdx) - refFuturesValue(currentFuturesIdx);
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
%                    nextX = nextX*(1.0 + dividendRatio);
                   nextX = nextX + dividendAmount;
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardLikely(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
            
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
%            %% renormalize Radon Nikodym Derivatives 
%             if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                 avgLHR = mean(likelyHoodRatio);
%                 likelyHoodRatio = likelyHoodRatio/avgLHR;
%             end
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
            %% importtant correction above
            
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
%                dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               dividendAmountRef = refFuturesValue(nextFuturesIdx) - refFuturesValue(currentFuturesIdx);
                
%                dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               dividendAmount = refFuturesValueSpot(nextFuturesIdx) - refFuturesValueSpot(currentFuturesIdx);
               
               for i=1:NMC
                   
                 %% dividendRatioRef start
                   if nextXIdxRef(i) ==1 
                       nextXRef = Ks(nextXIdxRef(i));
                   else
                       nextXRef = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextXRef = nextXRef + dividendAmountRef;
                   idxDummyRef = find(nextXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - nextXRef)/dK;
                       end
                   end

                   out.nextXIdxRef(i) = idxDummySRef;
                   out.nextXWeightRef(i) = weightRef;
                 
                 %% dividendRatioRef end
                 
                   if nextXIdxRef(i) ==1 
                       nextX = Ks(nextXIdxRef(i));
                   else
                       nextX = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
%                    nextX = nextX*(1.0 + dividendRatio);
                   nextX = nextX + dividendAmount;
                   
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == length(Ks) || idxH1 == 0
                    nextXWeight(i) = 0.0;
                else
%                     upperZ = norminv(cumProb(idxH1));
%                     lowerZ = norminv(cumProb(idxH1-1));
%                     sampleZ = norminv(uSample(i));
%                     nextXWeight(i) = (upperZ -sampleZ)/(upperZ-lowerZ);
%                     
                    nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1)-cumProb(idxH1-1));
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
%                dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               dividendAmount = refFuturesValue(nextFuturesIdx) - refFuturesValue(currentFuturesIdx);
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
%                    nextX = nextX*(1.0 + dividendRatio);
                   nextX = nextX + dividendAmount;
                   
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
%                    dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   dividendAmount = refFuturesValue(nextFuturesIdx)- refFuturesValue(currentFuturesIdx);
                   
                   for  idxzz= 1:length(dummyP)
%                        predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                       predictor(idxzz) = dummyP(idxzz) + 1.0 + dividendRatio;
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            if strcmp(params.params.volProxyRefYN,'YES')
                settleFutures = eqCOMDupireSpotGF.settleFuturesRef;
            else
                settleFutures = eqCOMDupireSpotGF.settleFutures;
            end
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            cValue = fwdPriceCNew;
            pValue = fwdPricePNew;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffLikely(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
            cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
            if idx ~= 1 
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                        cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    end
                end
              
                
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*cumulativeLikelyHoodRatio(idx11);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
                
            end    
            
            
        end
      
        function columnOut = MCPayoffLikelyRen(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
           %% sum(cumLHR2) = N - sum(cumLHR1); 
            cumulativeLikelyHoodRatio = zeros(modelStatesSize,1);
            
            dumMeasureSum = 0.0;
            dumMeasureSumPrev = 0.0;
            dumMeasureN = 0;
            if idx == 1 
                cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
                dumMeasureSum = sum(cumulativeLikelyHoodRatio);
                cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/dumMeasureSum*modelStatesSize;
                columnOut.cumLHR(:,idx) = cumulativeLikelyHoodRatio;
            else
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % dead path
                        dumMeasureSumPrev = dumMeasureSumPrev + columnIn.cumLHR(idx11,idx-1);
                        dumMeasureN = dumMeasureN + 1;
                    end
                end
                
                if dumMeasureN < modelStatesSize % if alive path normalize the relative measure
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                            dumMeasureSum = dumMeasureSum + cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                    
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = cumulativeLikelyHoodRatio(idx11)/(dumMeasureSum)*(modelStatesSize - dumMeasureSumPrev);
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                
                for idx11 =1:modelStatesSize % 1st early redemption
                        % every path is an alive path use all path to
                       
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                end
                
                
            elseif idx > 1 && idx < scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                     
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                    end
                end
              
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                    
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*columnOut.cumLHR(idx11,idx);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
   
                
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            dummyProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            eqCOMDupireSpotGF.localVolSurface.volProxy= ones(size(dummyProxy))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           initProb = zeros(1,gridSize);
           initProb(idxDummyS) = 1.0-weight;
           initProb(idxDummyS-1) = weight;
           
           initPriceC = zeros(length(Ks),1);
           initPriceP = zeros(length(Ks),1);
            
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           for idxh=1:length(Ks)
               initPriceC(idxh) = max(S0-Ks(idxh),0.0);
               initPriceP(idxh) = max(-S0+Ks(idxh),0.0);
           end
           
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           nextProb = initProb;
           nextPriceC = initPriceC;
           nextPriceP = initPriceP;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),...
%                                 nextXIdx,nextXWeight,nextProb,nextPriceC,nextPriceP,U(:,idx));
                            
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                            
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             

        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                else
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                end
                
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                            %LHR measure change onto original
                            contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                            unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
           cumLHR_avg = mean(columnOut.cumLHR);
           out.cumLHR_last = cumLHR_avg(end);
           
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx+1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx+1);
           
           out.hitValue = hitValue; 
           if stepdownParams.params('KIYN') == true
                out.unhitValue = hitValue;
           else
               out.unhitValue = unhitValue;
           end
           
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1);
           
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           cumulativeLikelyHoodRatio = ones(modelStatesSize,1);
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           %% likelyHoodRatio Calc
           for i=1:modelStatesSize
                payoffStateA.cashflow(i) = payoffStateA.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateB.cashflow(i) = payoffStateB.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateC.cashflow(i) =  payoffStateC.cashflow(i)*cumulativeLikelyHoodRatio(i);
           end
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            fwdPriceC = params.lastPriceC;
            fwdPRiceP = params.lastPriceP;
            
            optParams.params = params;
            optParams.params.GFType = -1;
            optParams.params.volProxyRefYN = 'NO';
            optParams.params.oneStepDt = 1.0/365.0;
            optParams.Ks = params.Ks;
            optParams.dK = params.dK;
            optParams.ipos = params.ipos;
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            optParams.idxNow = idxNow;
            %relevent volProxy
            volProxy   = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            
            dTDays = 0;
            
            if idxNow~=1
                fromTime = expiry(idxNow-1);
                toTime = maturity;
            else % idxNow == 1
                fromTime = 0;
                toTime = maturity;
                
            end
            
%             proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            outForward = BootStrapGFForward(eqCOMDupireSpotGF,volProxy,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams);
            
            cValue = outForward.fwdPriceCOut;
            pValue = outForward.fwdPricePOut;
            
            settleFutures = eqCOMDupireSpotGF.settleFutures;
            forward = settleFutures(idxNow);
            
            strikeSize = length(strikes);
            
            out.impVol = zeros(1,strikeSize);
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.impVol(i) = blackVolLBR(marKetPrice,forward,K, maturity/365.0,-1);
                else
                     marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                     out.impVol(i) = blackVolLBR(marKetPrice,forward,K, maturity/365.0,1);
                end
            end
            
            
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,targetExpiry,targetStrikes)
            
            params.expiry        = eqCOMDupireSpotGF.localVolSurface.expiry;
            params.pricingIdx    = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            params.pricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
            params.Ks            = eqCOMDupireSpotGF.localVolSurface.Ks;
            params.Ns = length(params.Ks); 
            params.dK = params.Ks(2) - params.Ks(1);
            
            targetStrikesPerExpirySize = size(targetStrikes,2);
           
            
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            lastPriceC = initPriceC;
            lastPriceP = initPriceP;
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                for idx=1:targetStrikesPerExpirySize
                    params.ipos(idx) = floor( (strikePerExpiry(idx) - params.Ks(1))/params.dK) + 1;  % add default 1
                    params.iweight(idx) = (strikePerExpiry(idx) - params.Ks(params.ipos(idx)))/params.dK;
                end
                
                params.lastPriceC = lastPriceC;
                params.lastPriceP = lastPriceP;
                
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                
                lastPriceC = outDummy.cValue;
                lastPriceP = outDummy.pValue;
                
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
%                     probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
%             out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
           fwdPriceC = optParams.lastPriceC;
           fwdPriceP = optParams.lastPriceP;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdPriceC,fwdPriceP,optParams);
           
           fwdPriceCNew = out.fwdPriceCOut;
           fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,optParams); 
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
               marketImpVol = optParams.params.blackVolRef;
           else
               marketImpVol = optParams.params.blackVol;
           end
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
                blackOTMPrices = optParams.params.blackOTMPricesRef;
           else
               blackOTMPrices = optParams.params.blackOTMPrices;
           end
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastPriceC,lastPriceP,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastPriceC = lastPriceC;
            optParams.lastPriceP = lastPriceP;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            if strcmp(params.volProxyRefYN,'YES')
                for i=1:params.strikeSize
                    tvar(i) = params.blackVolRef(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
            else
                for i=1:params.strikeSize
                    tvar(i) = params.blackVol(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
                
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            % Added 20190214 by sungwoo hong
            dummyOut = targetfunc(x);
            bootStrapOut.modelImpVolPost = dummyOut.modelImpVol;
            
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastPriceC,lastPriceP,optParams);
            
            bootStrapOut.lastPriceC = out.fwdPriceCOut;
            bootStrapOut.lastPriceP = out.fwdPricePOut;
            
        end
        
        
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            volSurfaceRef = black.volSurfaceRef;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackVolRef = zeros(expirySize,strikeSize);
            
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            
            blackOTMPricesRef = zeros(expirySize,strikeSize);
            fwdMoneynessRef = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end
            
            if  strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVolRef(k,j) = volSurfaceRef.volSurfaceR(k,j);
                        fwdMoneynessRef(k,j) = strike(j)/fwd;
                        marketStrikesRef(k,j) = strike(j);
                        
                        if fwdMoneynessRef(k,j) <= 1.0
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'P');
                        else
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'C');
                        end
                        
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.volSurfaceRef = volSurfaceRef;
            
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackOTMPricesRef = blackOTMPricesRef;
            
            params.blackVol = blackVol;
            
            params.blackVolRef = blackVolRef;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            params.fwdMoneynessRef = fwdMoneynessRef;
            
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            idxDummy = find(S0 >= params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end
            
            idxDummyS = max(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (S0 - params.Ks(idxDummyS))/params.dK;
            
          %% Ref Curve update
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            
            idxDummyRef = find(S0Ref >= params.Ks);
            if isempty(idxDummyRef)
                error('S0Ref is not covered in the grid K')
            end
            
            idxDummySRef = max(idxDummyRef);
            params.PricingidxRef = idxDummySRef;
            params.PricingWeightRef = (S0Ref - params.Ks(idxDummySRef))/params.dK;
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            params.volProxyRefYN = eqCOMDupireSpotGF.modelParams('volProxyRefYN');
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            
            out.fwdMoneynessRef = fwdMoneynessRef;
            
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyRef = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR') ...
                    || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            initPriceCRef = zeros(params.Ns,1);
            initPricePRef = zeros(params.Ns,1);
            
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            for idxh=1:params.Ns
                initPriceCRef(idxh) = max(S0Ref-params.Ks(idxh),0.0);
                initPricePRef(idxh) = max(-S0Ref+params.Ks(idxh),0.0);
            end
            
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPricesRef = blackOTMPricesRef;
            
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.blackVolRef =blackVolRef;
            
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.modelImpVolRef  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.interpBlackPricesRef = zeros(expirySize,strikeSize);
            out.dupireOTMPricesRef = zeros(expirySize,strikeSize);
            out.dupireBlackVolRef = zeros(expirySize,strikeSize);
            out.volErrorRef = zeros(expirySize,strikeSize);
            out.priceReRef = zeros(expirySize,strikeSize);
            out.priceReOrigRef = zeros(expirySize,strikeSize);
            out.marketStrikesRef = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.PricingidxRef = params.PricingidxRef;
            out.PricingWeightRef = params.PricingWeightRef;
            out.nIterRef = zeros(expirySize,1);
            out.localVolRef = zeros(expirySize,length(out.Ks));
            out.rmseTotalRef=0.0;
            out.fwdVolMseTotalRef = 0.0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
            case 'bootstrapLikely'
                    
                %% calibrate to reference forward Curve start
%                    
                    %vol proxy calibration
                    

                    
                    if strcmp(params.volProxyRefYN,'YES')

                        lastPriceCRef = initPriceCRef;
                        lastPricePRef = initPricePRef;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceCRef,lastPricePRef,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrigRef(i,j) = bootStrapOut.volProxy(j);
                                out.volProxyRef(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.iposRef(i,j)     = bootStrapOut.ipos(j);
                                out.volErrorRef(i,j) = bootStrapOut.volError(j);
                                out.marketImpVolRef(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVolRef(i,j) =  bootStrapOut.modelImpVol(j);
                                out.modelImpVolRefPost(i,j) =  bootStrapOut.modelImpVolPost(j);
                                out.interpBlackPricesRef(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPricesRef(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceReRef(i,j) = out.dupireOTMPricesRef(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrigRef(i,j) = out.dupireOTMPricesRef(i,j)/out.blackOTMPricesRef(i,j)-1.0;
                                out.marketStrikesRef(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIterRef(i) = bootStrapOut.nIter;
                            tempLocalVolRef = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVolRef(i,j) = tempLocalVolRef(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceCRef = bootStrapOut.lastPriceC;
                            lastPricePRef = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotalRef = out.rmseTotalRef + out.priceReOrigRef(j,k)*out.priceReOrigRef(j,k);
                                    out.fwdVolMseTotalRef = out.fwdVolMseTotalRef + out.volErrorRef(j,k)*out.volErrorRef(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotalRef = sqrt(out.rmseTotalRef/N);
                        out.fwdVolMseTotalRef = sqrt(out.fwdVolMseTotalRef/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxyRef = out.volProxyRef;
                        eqCOMDupireSpotGF.localVolSurface.iposRef = out.iposRef;
                        eqCOMDupireSpotGF.localVolSurface.localVolRef = out.localVolRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingidxRef = out.PricingidxRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeightRef = out.PricingWeightRef;

                        %% calibrate to spot forward curve end
                    
                    else
                     %% calibrate to spot forward curve start

                        lastPriceC = initPriceC;
                        lastPriceP = initPriceP;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                                out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.ipos(i,j)     = bootStrapOut.ipos(j);
                                out.volError(i,j) = bootStrapOut.volError(j);
                                out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                                out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIter(i) = bootStrapOut.nIter;
                            tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVol(i,j) = tempLocalVol(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceC = bootStrapOut.lastPriceC;
                            lastPriceP = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                    out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                        eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                        eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                        eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
    
                        eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                        eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                        eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                        eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;

                        eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;

                      %% calibrate to spot forward curve end   
                    end
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMFLSimple < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        %Likely
        settleFuturesRef
        
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMFLSimple(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            localVol = interp1(volProxyKs,volProxy,Ks','linear','extrap');
            
%             for i=1:length(Ks)
%                 localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
%             end   
                
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           if strcmp(optParams.params.volProxyRefYN,'YES') 
               refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           else
               refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           end
           
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
               
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           dK = optParams.dK;
           priceC = fwdPriceC;
           priceP = fwdPRiceP;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        priceC,priceP,optParams);

               priceC = outGF.newPriceC;
               priceP = outGF.newPriceP;
               
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = priceC;
                   dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                       priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                       priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                       priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);
                       
                       if priceC(idxzz) < 0
                            priceC(idxzz) = 0.0;
                       end
                       
                       if priceP(idxzz) < 0
                           priceP(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           out.fwdPriceCOut = priceC;
           out.fwdPricePOut = priceP;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,priceC,priceP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(priceC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(priceC);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newPriceC = A_exp1*priceC;
                newPriceP = A_exp1*priceP;
            
            end
            
            out.newPriceC = newPriceC;
            out.newPriceP = newPriceP;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)*(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)*(1.0 + dividendRatio)-Ks(NGP))/dK;
                       lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       
                       if lastPrice(idxzz) < 0
                            lastPrice(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYNFlag);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1),volProxyRefYN);
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            if strcmp(volProxyRefYNFlag,'YES')
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxyRef(idxNow,:);
            else
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            end
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            
            volProxy   = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            volProxyKs = eqCOMDupireSpotGF.localVolSurface.marketStrikes(idxNow,:);
            
            localVol = interp1(volProxyKs,volProxy,x','linear','extrap');
            
            
%             localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
%             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
%             
            
%             for ii =1:length(x)
%                 localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
%             end
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,...
                        lastProb,lastPriceC, lastPriceP,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            
            nextProb = lastProb*condProb;
            nextPriceC = condProb*lastPriceC;
            % Check the ex-dividend date & if it is then adjust prob accordingly 
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               dummyProb = nextProb;
               dummyC = nextPriceC; 
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;

               if dividendRatio > 0
                   
               end
               for  idxzz= 1:length(dummyProb)
                   NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                   if NGP < 1
                       NGP = 1;
                   end

                   if NGP > length(dummyC)-1
                       NGP = length(dummyC)-1;
                   end

                   weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                   priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                   priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                   priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                   priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);

                   if priceC(idxzz) < 0
                        priceC(idxzz) = 0.0;
                   end

                   if priceP(idxzz) < 0
                       priceP(idxzz) = 0.0;
                   end

               end
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalCumPerExpiry(nextProb,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nPoints = length(Ks);
            
            debugDx = zeros(NMC,1);
            debugIdx1 = zeros(NMC,1);
            debugIdx2 = zeros(NMC,1);
            debugWeight1 = zeros(NMC,1);
            debugWeight2 = zeros(NMC,1);
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                
                idxH1 = min(find(uSample(i) < cumProb1));
                idxH2 = min(find(uSample(i) < cumProb2));
                debugDx(i) = idxH1-idxH2;
                debugIdx1(i) = idxH1;
                debugIdx2(i) = idxH2;
                
                nextX = (1.0-lastXWeight(i))*Ks(idxH1) + lastXWeight(i)*Ks(idxH2);
                idxDummy = find(nextX < Ks);
                if isempty(idxDummy)
                    error('nextX is not covered in the grid K')
                end
                
                idxDummyS = min(idxDummy);
                weight = (Ks(idxDummyS)-nextX)/dK;
                nextXIdx(i) = idxDummyS;
                nextXWeight(i) = weight;
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;

            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardLikely(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
            
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
%            %% renormalize Radon Nikodym Derivatives 
%             if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                 avgLHR = mean(likelyHoodRatio);
%                 likelyHoodRatio = likelyHoodRatio/avgLHR;
%             end
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
            %% importtant correction above
            
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   
                 %% dividendRatioRef start
                   if nextXIdxRef(i) ==1 
                       nextXRef = Ks(nextXIdxRef(i));
                   else
                       nextXRef = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextXRef = nextXRef*(1.0 + dividendRatioRef);
                   idxDummyRef = find(nextXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - nextXRef)/dK;
                       end
                   end

                   out.nextXIdxRef(i) = idxDummySRef;
                   out.nextXWeightRef(i) = weightRef;
                 
                 %% dividendRatioRef end
                 
                   if nextXIdxRef(i) ==1 
                       nextX = Ks(nextXIdxRef(i));
                   else
                       nextX = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == 1
                    nextXWeight(i) = 0.0;
                else

                    sampleZ = uSample(i);
                    
                    nextXWeight(i) = (cumProb(idxH1) -sampleZ)/(cumProb(idxH1)-cumProb(idxH1-1));
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyP)
                       predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            if strcmp(params.params.volProxyRefYN,'YES')
                settleFutures = eqCOMDupireSpotGF.settleFuturesRef;
            else
                settleFutures = eqCOMDupireSpotGF.settleFutures;
            end
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            cValue = fwdPriceCNew;
            pValue = fwdPricePNew;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffLikely(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
            cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
            if idx ~= 1 
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                        cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    end
                end
              
                
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*cumulativeLikelyHoodRatio(idx11);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
                
            end    
            
            
        end
      
        function columnOut = MCPayoffLikelyRen(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
           %% sum(cumLHR2) = N - sum(cumLHR1); 
            cumulativeLikelyHoodRatio = zeros(modelStatesSize,1);
            
            dumMeasureSum = 0.0;
            dumMeasureSumPrev = 0.0;
            dumMeasureN = 0;
            if idx == 1 
                cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
                dumMeasureSum = sum(cumulativeLikelyHoodRatio);
                cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/dumMeasureSum*modelStatesSize;
                columnOut.cumLHR(:,idx) = cumulativeLikelyHoodRatio;
            else
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % dead path
                        dumMeasureSumPrev = dumMeasureSumPrev + columnIn.cumLHR(idx11,idx-1);
                        dumMeasureN = dumMeasureN + 1;
                    end
                end
                
                if dumMeasureN < modelStatesSize % if alive path normalize the relative measure
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                            dumMeasureSum = dumMeasureSum + cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                    
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = cumulativeLikelyHoodRatio(idx11)/(dumMeasureSum)*(modelStatesSize - dumMeasureSumPrev);
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                
                for idx11 =1:modelStatesSize % 1st early redemption
                        % every path is an alive path use all path to
                       
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                end
                
                
            elseif idx > 1 && idx < scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                     
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                    end
                end
              
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                    
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*columnOut.cumLHR(idx11,idx);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
   
                
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            dummyProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            eqCOMDupireSpotGF.localVolSurface.volProxy= ones(size(dummyProxy))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           initProb = zeros(1,gridSize);
           initProb(idxDummyS) = 1.0-weight;
           initProb(idxDummyS-1) = weight;
           
           initPriceC = zeros(length(Ks),1);
           initPriceP = zeros(length(Ks),1);
            
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           for idxh=1:length(Ks)
               initPriceC(idxh) = max(S0-Ks(idxh),0.0);
               initPriceP(idxh) = max(-S0+Ks(idxh),0.0);
           end
           
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           nextProb = initProb;
           nextPriceC = initPriceC;
           nextPriceP = initPriceP;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),...
%                                 nextXIdx,nextXWeight,nextProb,nextPriceC,nextPriceP,U(:,idx));
                            
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                            
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             

        
        function out = computeStepdown1SMCMCINT(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
%                                 nextXIdx,nextXWeight,U(:,idx));
                            
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
%                     nextXIdxRef = mcmcOut.nextXIdxRef;
%                     nextXWeightRef = mcmcOut.nextXWeightRef;
                    
%                     periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
%                 if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                     columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
%                 else
%                     columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
%                 end
                
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
%                 cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
%                             %LHR measure change onto original
%                             contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
%                             unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
%            cumLHR_avg = mean(columnOut.cumLHR);
%            out.cumLHR_last = cumLHR_avg(end);
           
        end
        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
                            
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                else
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                end
                
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                            %LHR measure change onto original
                            contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                            unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
           cumLHR_avg = mean(columnOut.cumLHR);
           out.cumLHR_last = cumLHR_avg(end);
           
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx+1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx+1);
           
           out.hitValue = hitValue; 
           if stepdownParams.params('KIYN') == true
                out.unhitValue = hitValue;
           else
               out.unhitValue = unhitValue;
           end
           
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1);
           
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           cumulativeLikelyHoodRatio = ones(modelStatesSize,1);
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           %% likelyHoodRatio Calc
           for i=1:modelStatesSize
                payoffStateA.cashflow(i) = payoffStateA.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateB.cashflow(i) = payoffStateB.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateC.cashflow(i) =  payoffStateC.cashflow(i)*cumulativeLikelyHoodRatio(i);
           end
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            fwdPriceC = params.lastPriceC;
            fwdPRiceP = params.lastPriceP;
            
            optParams.params = params;
            optParams.params.GFType = -1;
            optParams.params.volProxyRefYN = 'NO';
            optParams.params.oneStepDt = 1.0/365.0;
            optParams.Ks = params.Ks;
            optParams.dK = params.dK;
            optParams.ipos = params.ipos;
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            optParams.idxNow = idxNow;
            %relevent volProxy
            volProxy   = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            
            dTDays = 0;
            
            if idxNow~=1
                fromTime = expiry(idxNow-1);
                toTime = maturity;
            else % idxNow == 1
                fromTime = 0;
                toTime = maturity;
                
            end
            
%             proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            outForward = BootStrapGFForward(eqCOMDupireSpotGF,volProxy,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams);
            
            cValue = outForward.fwdPriceCOut;
            pValue = outForward.fwdPricePOut;
            
            settleFutures = eqCOMDupireSpotGF.settleFutures;
            forward = settleFutures(idxNow);
            
            strikeSize = length(strikes);
            
            out.impVol = zeros(1,strikeSize);
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.impVol(i) = blackVolLBR(marKetPrice,forward,K, maturity/365.0,-1);
                else
                     marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                     out.impVol(i) = blackVolLBR(marKetPrice,forward,K, maturity/365.0,1);
                end
            end
            
            
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,targetExpiry,targetStrikes)
            
            params.expiry        = eqCOMDupireSpotGF.localVolSurface.expiry;
            params.pricingIdx    = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            params.pricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
            params.Ks            = eqCOMDupireSpotGF.localVolSurface.Ks;
            params.Ns = length(params.Ks); 
            params.dK = params.Ks(2) - params.Ks(1);
            
            targetStrikesPerExpirySize = size(targetStrikes,2);
           
            
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            lastPriceC = initPriceC;
            lastPriceP = initPriceP;
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                for idx=1:targetStrikesPerExpirySize
                    params.ipos(idx) = floor( (strikePerExpiry(idx) - params.Ks(1))/params.dK) + 1;  % add default 1
                    params.iweight(idx) = (strikePerExpiry(idx) - params.Ks(params.ipos(idx)))/params.dK;
                end
                
                params.lastPriceC = lastPriceC;
                params.lastPriceP = lastPriceP;
                
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                
                lastPriceC = outDummy.cValue;
                lastPriceP = outDummy.pValue;
                
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
%                     probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
%             out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
           fwdPriceC = optParams.lastPriceC;
           fwdPriceP = optParams.lastPriceP;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdPriceC,fwdPriceP,optParams);
           
           fwdPriceCNew = out.fwdPriceCOut;
           fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,optParams); 
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
               marketImpVol = optParams.params.blackVolRef;
           else
               marketImpVol = optParams.params.blackVol;
           end
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
                blackOTMPrices = optParams.params.blackOTMPricesRef;
           else
               blackOTMPrices = optParams.params.blackOTMPrices;
           end
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastPriceC,lastPriceP,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastPriceC = lastPriceC;
            optParams.lastPriceP = lastPriceP;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            if strcmp(params.volProxyRefYN,'YES')
                for i=1:params.strikeSize
                    tvar(i) = params.blackVolRef(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
            else
                for i=1:params.strikeSize
                    tvar(i) = params.blackVol(idxNow,i);
                    lb(i) = 0.01;
                    ub(i) = 1.0;
                end
                
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            % Added 20190214 by sungwoo hong
            dummyOut = targetfunc(x);
            bootStrapOut.modelImpVolPost = dummyOut.modelImpVol;
            
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastPriceC,lastPriceP,optParams);
            
            bootStrapOut.lastPriceC = out.fwdPriceCOut;
            bootStrapOut.lastPriceP = out.fwdPricePOut;
            
        end
        
        
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            volSurfaceRef = black.volSurfaceRef;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackVolRef = zeros(expirySize,strikeSize);
            
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            
            blackOTMPricesRef = zeros(expirySize,strikeSize);
            fwdMoneynessRef = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end
            
            if  strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVolRef(k,j) = volSurfaceRef.volSurfaceR(k,j);
                        fwdMoneynessRef(k,j) = strike(j)/fwd;
                        marketStrikesRef(k,j) = strike(j);
                        
                        if fwdMoneynessRef(k,j) <= 1.0
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'P');
                        else
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVolRef(k,j),'C');
                        end
                        
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.volSurfaceRef = volSurfaceRef;
            
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackOTMPricesRef = blackOTMPricesRef;
            
            params.blackVol = blackVol;
            
            params.blackVolRef = blackVolRef;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            params.fwdMoneynessRef = fwdMoneynessRef;
            
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            idxDummy = find(S0 >= params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end
            
            idxDummyS = max(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (S0 - params.Ks(idxDummyS))/params.dK;
            
          %% Ref Curve update
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            
            idxDummyRef = find(S0Ref >= params.Ks);
            if isempty(idxDummyRef)
                error('S0Ref is not covered in the grid K')
            end
            
            idxDummySRef = max(idxDummyRef);
            params.PricingidxRef = idxDummySRef;
            params.PricingWeightRef = (S0Ref - params.Ks(idxDummySRef))/params.dK;
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            params.volProxyRefYN = eqCOMDupireSpotGF.modelParams('volProxyRefYN');
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            
            out.fwdMoneynessRef = fwdMoneynessRef;
            
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyRef = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR') ...
                    || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            initPriceCRef = zeros(params.Ns,1);
            initPricePRef = zeros(params.Ns,1);
            
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            for idxh=1:params.Ns
                initPriceCRef(idxh) = max(S0Ref-params.Ks(idxh),0.0);
                initPricePRef(idxh) = max(-S0Ref+params.Ks(idxh),0.0);
            end
            
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPricesRef = blackOTMPricesRef;
            
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.blackVolRef =blackVolRef;
            
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.modelImpVolRef  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.interpBlackPricesRef = zeros(expirySize,strikeSize);
            out.dupireOTMPricesRef = zeros(expirySize,strikeSize);
            out.dupireBlackVolRef = zeros(expirySize,strikeSize);
            out.volErrorRef = zeros(expirySize,strikeSize);
            out.priceReRef = zeros(expirySize,strikeSize);
            out.priceReOrigRef = zeros(expirySize,strikeSize);
            out.marketStrikesRef = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.PricingidxRef = params.PricingidxRef;
            out.PricingWeightRef = params.PricingWeightRef;
            out.nIterRef = zeros(expirySize,1);
            out.localVolRef = zeros(expirySize,length(out.Ks));
            out.rmseTotalRef=0.0;
            out.fwdVolMseTotalRef = 0.0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
            case 'bootstrapLikely'
                    
                %% calibrate to reference forward Curve start
%                    
                    %vol proxy calibration
                    

                    
                    if strcmp(params.volProxyRefYN,'YES')

                        lastPriceCRef = initPriceCRef;
                        lastPricePRef = initPricePRef;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceCRef,lastPricePRef,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrigRef(i,j) = bootStrapOut.volProxy(j);
                                out.volProxyRef(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.iposRef(i,j)     = bootStrapOut.ipos(j);
                                out.volErrorRef(i,j) = bootStrapOut.volError(j);
                                out.marketImpVolRef(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVolRef(i,j) =  bootStrapOut.modelImpVol(j);
                                out.modelImpVolRefPost(i,j) =  bootStrapOut.modelImpVolPost(j);
                                out.interpBlackPricesRef(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPricesRef(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceReRef(i,j) = out.dupireOTMPricesRef(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrigRef(i,j) = out.dupireOTMPricesRef(i,j)/out.blackOTMPricesRef(i,j)-1.0;
                                out.marketStrikesRef(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIterRef(i) = bootStrapOut.nIter;
                            tempLocalVolRef = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVolRef(i,j) = tempLocalVolRef(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceCRef = bootStrapOut.lastPriceC;
                            lastPricePRef = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotalRef = out.rmseTotalRef + out.priceReOrigRef(j,k)*out.priceReOrigRef(j,k);
                                    out.fwdVolMseTotalRef = out.fwdVolMseTotalRef + out.volErrorRef(j,k)*out.volErrorRef(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotalRef = sqrt(out.rmseTotalRef/N);
                        out.fwdVolMseTotalRef = sqrt(out.fwdVolMseTotalRef/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxyRef = out.volProxyRef;
                        eqCOMDupireSpotGF.localVolSurface.iposRef = out.iposRef;
                        eqCOMDupireSpotGF.localVolSurface.localVolRef = out.localVolRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingidxRef = out.PricingidxRef;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeightRef = out.PricingWeightRef;

                        %% calibrate to spot forward curve end
                    
                    else
                     %% calibrate to spot forward curve start

                        lastPriceC = initPriceC;
                        lastPriceP = initPriceP;

                        for i=1:expirySize
                            if  i ~= 1
                                fromTime = params.expiry(i-1);
                                toTime   = params.expiry(i);
                            else
                                fromTime = 0;
                                toTime = params.expiry(1);
                            end

                            bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);

                            % we apply floor and cap for the volProxy

                            for j=1:strikeSize
                                out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                                out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                                out.ipos(i,j)     = bootStrapOut.ipos(j);
                                out.volError(i,j) = bootStrapOut.volError(j);
                                out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                                out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                                out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                                out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                                out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                                out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                                out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                            end

                            out.nIter(i) = bootStrapOut.nIter;
                            tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                            for j=1:params.Ns
    %                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                                out.localVol(i,j) = tempLocalVol(j);
                            end

    %                         out.condProb(i,:,:) = bootStrapOut.condProb;
                            % Initial Payoff for the next period
                            lastPriceC = bootStrapOut.lastPriceC;
                            lastPriceP = bootStrapOut.lastPriceP;

                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if eqCOMDupireSpotGF.useYN(j,k) > 0
                                    out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                    out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);

                        % assigning the calibrated volProxy to the local vol
                        % surface
                        eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                        eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                        eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                        eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                        eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
    
                        eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                        eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                        eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                        eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;

                        eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;

                      %% calibrate to spot forward curve end   
                    end
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMFLBack < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        %Likely
        settleFuturesRef
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMFLBack(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            for i=1:length(Ks)
                localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
            end   
                
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           if strcmp(optParams.params.volProxyRefYN,'YES') 
               refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           else
               refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           end
           
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
               
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           dK = optParams.dK;
           priceC = fwdPriceC;
           priceP = fwdPRiceP;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        priceC,priceP,optParams);

               priceC = outGF.newPriceC;
               priceP = outGF.newPriceP;
               
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = priceC;
                   dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                       priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                       priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                       priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);
                       
                       if priceC(idxzz) < 0
                            priceC(idxzz) = 0.0;
                       end
                       
                       if priceP(idxzz) < 0
                           priceP(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           out.fwdPriceCOut = priceC;
           out.fwdPricePOut = priceP;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,priceC,priceP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(priceC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(priceC);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newPriceC = A_exp1*priceC;
                newPriceP = A_exp1*priceP;
            
            end
            
            out.newPriceC = newPriceC;
            out.newPriceP = newPriceP;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)*(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)*(1.0 + dividendRatio)-Ks(NGP))/dK;
                       lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       
                       if lastPrice(idxzz) < 0
                            lastPrice(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYNFlag);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1),volProxyRefYN);
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            if strcmp(volProxyRefYNFlag,'YES')
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxyRef(idxNow,:);
            else
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            end
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            
            for ii =1:length(x)
                localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
            end
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,...
                        lastProb,lastPriceC, lastPriceP,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            
            nextProb = lastProb*condProb;
            nextPriceC = condProb*lastPriceC;
            % Check the ex-dividend date & if it is then adjust prob accordingly 
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               dummyProb = nextProb;
               dummyC = nextPriceC; 
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;

               if dividendRatio > 0
                   
               end
               for  idxzz= 1:length(dummyProb)
                   NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                   if NGP < 1
                       NGP = 1;
                   end

                   if NGP > length(dummyC)-1
                       NGP = length(dummyC)-1;
                   end

                   weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                   priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                   priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                   priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                   priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);

                   if priceC(idxzz) < 0
                        priceC(idxzz) = 0.0;
                   end

                   if priceP(idxzz) < 0
                       priceP(idxzz) = 0.0;
                   end

               end
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalCumPerExpiry(nextProb,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nPoints = length(Ks);
            
            debugDx = zeros(NMC,1);
            debugIdx1 = zeros(NMC,1);
            debugIdx2 = zeros(NMC,1);
            debugWeight1 = zeros(NMC,1);
            debugWeight2 = zeros(NMC,1);
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                
                idxH1 = min(find(uSample(i) < cumProb1));
                idxH2 = min(find(uSample(i) < cumProb2));
                debugDx(i) = idxH1-idxH2;
                debugIdx1(i) = idxH1;
                debugIdx2(i) = idxH2;
                
                nextX = (1.0-lastXWeight(i))*Ks(idxH1) + lastXWeight(i)*Ks(idxH2);
                idxDummy = find(nextX < Ks);
                if isempty(idxDummy)
                    error('nextX is not covered in the grid K')
                end
                
                idxDummyS = min(idxDummy);
                weight = (Ks(idxDummyS)-nextX)/dK;
                nextXIdx(i) = idxDummyS;
                nextXWeight(i) = weight;
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;

            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardLikely(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
            
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            volProxyRefYN = 'YES';
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
%            %% renormalize Radon Nikodym Derivatives 
%             if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                 avgLHR = mean(likelyHoodRatio);
%                 likelyHoodRatio = likelyHoodRatio/avgLHR;
%             end
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
            %% importtant correction above
            
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   
                 %% dividendRatioRef start
                   if nextXIdxRef(i) ==1 
                       nextXRef = Ks(nextXIdxRef(i));
                   else
                       nextXRef = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextXRef = nextXRef*(1.0 + dividendRatioRef);
                   idxDummyRef = find(nextXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - nextXRef)/dK;
                       end
                   end

                   out.nextXIdxRef(i) = idxDummySRef;
                   out.nextXWeightRef(i) = weightRef;
                 
                 %% dividendRatioRef end
                 
                   if nextXIdxRef(i) ==1 
                       nextX = Ks(nextXIdxRef(i));
                   else
                       nextX = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == length(Ks) || idxH1 == 0
                    nextXWeight(i) = 0.0;
                else
                    upperZ = norminv(cumProb(idxH1));
                    lowerZ = norminv(cumProb(idxH1-1));
                    sampleZ = norminv(uSample(i));
                    nextXWeight(i) = (upperZ -sampleZ)/(upperZ-lowerZ);
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyP)
                       predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            if strcmp(params.params.volProxyRefYN,'YES')
                settleFutures = eqCOMDupireSpotGF.settleFuturesRef;
            else
                settleFutures = eqCOMDupireSpotGF.settleFutures;
            end
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            cValue = fwdPriceCNew;
            pValue = fwdPricePNew;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffLikely(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
            cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
            if idx ~= 1 
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                        cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    end
                end
              
                
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*cumulativeLikelyHoodRatio(idx11);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
                
            end    
            
            
        end
      
        function columnOut = MCPayoffLikelyRen(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
           %% sum(cumLHR2) = N - sum(cumLHR1); 
            cumulativeLikelyHoodRatio = zeros(modelStatesSize,1);
            
            dumMeasureSum = 0.0;
            dumMeasureSumPrev = 0.0;
            dumMeasureN = 0;
            if idx == 1 
                cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
                dumMeasureSum = sum(cumulativeLikelyHoodRatio);
                cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/dumMeasureSum*modelStatesSize;
                columnOut.cumLHR(:,idx) = cumulativeLikelyHoodRatio;
            else
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % dead path
                        dumMeasureSumPrev = dumMeasureSumPrev + columnIn.cumLHR(idx11,idx-1);
                        dumMeasureN = dumMeasureN + 1;
                    end
                end
                
                if dumMeasureN < modelStatesSize % if alive path normalize the relative measure
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                            dumMeasureSum = dumMeasureSum + cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                    
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = cumulativeLikelyHoodRatio(idx11)/(dumMeasureSum)*(modelStatesSize - dumMeasureSumPrev);
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                
                for idx11 =1:modelStatesSize % 1st early redemption
                        % every path is an alive path use all path to
                       
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                end
                
                
            elseif idx > 1 && idx < scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                     
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                    end
                end
              
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                    
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*columnOut.cumLHR(idx11,idx);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
   
                
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            eqCOMDupireSpotGF.localVolSurface.volProxy = ones(size(fwdMoneyness))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           initProb = zeros(1,gridSize);
           initProb(idxDummyS) = 1.0-weight;
           initProb(idxDummyS-1) = weight;
           
           initPriceC = zeros(length(Ks),1);
           initPriceP = zeros(length(Ks),1);
            
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           for idxh=1:length(Ks)
               initPriceC(idxh) = max(S0-Ks(idxh),0.0);
               initPriceP(idxh) = max(-S0+Ks(idxh),0.0);
           end
           
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           nextProb = initProb;
           nextPriceC = initPriceC;
           nextPriceP = initPriceP;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),...
%                                 nextXIdx,nextXWeight,nextProb,nextPriceC,nextPriceP,U(:,idx));
                            
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                            
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             

        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                else
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                end
                
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                            %LHR measure change onto original
                            contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                            unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
           cumLHR_avg = mean(columnOut.cumLHR);
           out.cumLHR_last = cumLHR_avg(end);
           
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx+1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx+1);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1);
           
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           cumulativeLikelyHoodRatio = ones(modelStatesSize,1);
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           %% likelyHoodRatio Calc
           for i=1:modelStatesSize
                payoffStateA.cashflow(i) = payoffStateA.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateB.cashflow(i) = payoffStateB.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateC.cashflow(i) =  payoffStateC.cashflow(i)*cumulativeLikelyHoodRatio(i);
           end
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)

            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
           fwdPriceC = optParams.lastPriceC;
           fwdPriceP = optParams.lastPriceP;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdPriceC,fwdPriceP,optParams);
           
           fwdPriceCNew = out.fwdPriceCOut;
           fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,optParams); 
           
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
                blackOTMPrices = optParams.params.blackOTMPricesRef;
           else
               blackOTMPrices = optParams.params.blackOTMPrices;
           end
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastPriceC,lastPriceP,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastPriceC = lastPriceC;
            optParams.lastPriceP = lastPriceP;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastPriceC,lastPriceP,optParams);
            
            bootStrapOut.lastPriceC = out.fwdPriceCOut;
            bootStrapOut.lastPriceP = out.fwdPricePOut;
            
        end
        
        
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            
            blackOTMPricesRef = zeros(expirySize,strikeSize);
            fwdMoneynessRef = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end
            
            if  strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneynessRef(k,j) = strike(j)/fwd;
                        marketStrikesRef(k,j) = strike(j);
                        
                        if fwdMoneynessRef(k,j) <= 1.0
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVol(k,j),'C');
                        end
                        
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackOTMPricesRef = blackOTMPricesRef;
            
            params.blackVol = blackVol;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            params.fwdMoneynessRef = fwdMoneynessRef;
            
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            idxDummy = find(S0 >= params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end
            
            idxDummyS = max(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (S0 - params.Ks(idxDummyS))/params.dK;
            
          %% Ref Curve update
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            
            idxDummyRef = find(S0Ref >= params.Ks);
            if isempty(idxDummyRef)
                error('S0Ref is not covered in the grid K')
            end
            
            idxDummySRef = max(idxDummyRef);
            params.PricingidxRef = idxDummySRef;
            params.PricingWeightRef = (S0Ref - params.Ks(idxDummySRef))/params.dK;
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            
            out.fwdMoneynessRef = fwdMoneynessRef;
            
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyRef = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR') ...
                    || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            initPriceCRef = zeros(params.Ns,1);
            initPricePRef = zeros(params.Ns,1);
            
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            for idxh=1:params.Ns
                initPriceCRef(idxh) = max(S0Ref-params.Ks(idxh),0.0);
                initPricePRef(idxh) = max(-S0Ref+params.Ks(idxh),0.0);
            end
            
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPricesRef = blackOTMPricesRef;
            
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.modelImpVolRef  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.interpBlackPricesRef = zeros(expirySize,strikeSize);
            out.dupireOTMPricesRef = zeros(expirySize,strikeSize);
            out.dupireBlackVolRef = zeros(expirySize,strikeSize);
            out.volErrorRef = zeros(expirySize,strikeSize);
            out.priceReRef = zeros(expirySize,strikeSize);
            out.priceReOrigRef = zeros(expirySize,strikeSize);
            out.marketStrikesRef = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.PricingidxRef = params.PricingidxRef;
            out.PricingWeightRef = params.PricingWeightRef;
            out.nIterRef = zeros(expirySize,1);
            out.localVolRef = zeros(expirySize,length(out.Ks));
            out.rmseTotalRef=0.0;
            out.fwdVolMseTotalRef = 0.0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
            case 'bootstrapLikely'
                    
                %% calibrate to reference forward Curve start
%                    
                    %vol proxy calibration
                    
                    params.volProxyRefYN = 'YES';
                    
                    lastPriceCRef = initPriceCRef;
                    lastPricePRef = initPricePRef;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceCRef,lastPricePRef,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrigRef(i,j) = bootStrapOut.volProxy(j);
                            out.volProxyRef(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.iposRef(i,j)     = bootStrapOut.ipos(j);
                            out.volErrorRef(i,j) = bootStrapOut.volError(j);
                            out.marketImpVolRef(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVolRef(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPricesRef(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPricesRef(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceReRef(i,j) = out.dupireOTMPricesRef(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrigRef(i,j) = out.dupireOTMPricesRef(i,j)/out.blackOTMPricesRef(i,j)-1.0;
                            out.marketStrikesRef(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIterRef(i) = bootStrapOut.nIter;
                        tempLocalVolRef = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVolRef(i,j) = tempLocalVolRef(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceCRef = bootStrapOut.lastPriceC;
                        lastPricePRef = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotalRef = out.rmseTotalRef + out.priceReOrigRef(j,k)*out.priceReOrigRef(j,k);
                                out.fwdVolMseTotalRef = out.fwdVolMseTotalRef + out.volErrorRef(j,k)*out.volErrorRef(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotalRef = sqrt(out.rmseTotalRef/N);
                    out.fwdVolMseTotalRef = sqrt(out.fwdVolMseTotalRef/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxyRef = out.volProxyRef;
                    eqCOMDupireSpotGF.localVolSurface.iposRef = out.iposRef;
                    eqCOMDupireSpotGF.localVolSurface.localVolRef = out.localVolRef;
                    eqCOMDupireSpotGF.localVolSurface.PricingidxRef = out.PricingidxRef;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeightRef = out.PricingWeightRef;
%                     eqCOMDupireSpotGF.localVolSurface.probMeshRef = out.probMeshRef;
%                     eqCOMDupireSpotGF.localVolSurface.condProbRef = out.condProbRef;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
%                     eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
%                     eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
%                     eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
%                     eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
%                     eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    
                 %% calibrate to spot forward curve end
                    
                 %% calibrate to spot forward curve start
                    params.volProxyRefYN = 'NO';
                    
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
%                     eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
%                     eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                  %% calibrate to spot forward curve end        
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMFL < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
        
        %Likely
        settleFuturesRef
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMFL(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            for i=1:length(Ks)
                localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
            end   
                
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           if strcmp(optParams.params.volProxyRefYN,'YES') 
               refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           else
               refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           end
           
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
               
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           dK = optParams.dK;
           priceC = fwdPriceC;
           priceP = fwdPRiceP;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        priceC,priceP,optParams);

               priceC = outGF.newPriceC;
               priceP = outGF.newPriceP;
               
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = priceC;
                   dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                       priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                       priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                       priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);
                       
                       if priceC(idxzz) < 0
                            priceC(idxzz) = 0.0;
                       end
                       
                       if priceP(idxzz) < 0
                           priceP(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           out.fwdPriceCOut = priceC;
           out.fwdPricePOut = priceP;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,priceC,priceP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(priceC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(priceC);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newPriceC = A_exp1*priceC;
                newPriceP = A_exp1*priceP;
            
            end
            
            out.newPriceC = newPriceC;
            out.newPriceP = newPriceP;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)*(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)*(1.0 + dividendRatio)-Ks(NGP))/dK;
                       lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       
                       if lastPrice(idxzz) < 0
                            lastPrice(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYNFlag);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1),volProxyRefYN);
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime,volProxyRefYN)
            
            volProxyRefYNFlag = 'NO';
            if nargin > 3
                volProxyRefYNFlag = volProxyRefYN;
            end
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            if strcmp(volProxyRefYNFlag,'YES')
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxyRef(idxNow,:);
            else
                volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            end
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            
            for ii =1:length(x)
                localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
            end
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,...
                        lastProb,lastPriceC, lastPriceP,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            
            nextProb = lastProb*condProb;
            nextPriceC = condProb*lastPriceC;
            % Check the ex-dividend date & if it is then adjust prob accordingly 
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               dummyProb = nextProb;
               dummyC = nextPriceC; 
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;

               if dividendRatio > 0
                   
               end
               for  idxzz= 1:length(dummyProb)
                   NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                   if NGP < 1
                       NGP = 1;
                   end

                   if NGP > length(dummyC)-1
                       NGP = length(dummyC)-1;
                   end

                   weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                   priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                   priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                   priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                   priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);

                   if priceC(idxzz) < 0
                        priceC(idxzz) = 0.0;
                   end

                   if priceP(idxzz) < 0
                       priceP(idxzz) = 0.0;
                   end

               end
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalCumPerExpiry(nextProb,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nPoints = length(Ks);
            
            debugDx = zeros(NMC,1);
            debugIdx1 = zeros(NMC,1);
            debugIdx2 = zeros(NMC,1);
            debugWeight1 = zeros(NMC,1);
            debugWeight2 = zeros(NMC,1);
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                
                idxH1 = min(find(uSample(i) < cumProb1));
                idxH2 = min(find(uSample(i) < cumProb2));
                debugDx(i) = idxH1-idxH2;
                debugIdx1(i) = idxH1;
                debugIdx2(i) = idxH2;
                
                nextX = (1.0-lastXWeight(i))*Ks(idxH1) + lastXWeight(i)*Ks(idxH2);
                idxDummy = find(nextX < Ks);
                if isempty(idxDummy)
                    error('nextX is not covered in the grid K')
                end
                
                idxDummyS = min(idxDummy);
                weight = (Ks(idxDummyS)-nextX)/dK;
                nextXIdx(i) = idxDummyS;
                nextXWeight(i) = weight;
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;

            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardLikely(eqCOMDupireSpotGF,fromTime,toTime,lastXIdxRef,lastXWeightRef,lastXIdx,lastXWeight,U)
            
                     
          %% find the futures roll overDates between fromTime to toTime;
          
           refFuturesCurve = eqCOMDupireSpotGF.referenceForwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           refFuturesCurveSpot = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpirySpot = refFuturesCurveSpot(:,1);
           refFuturesValueSpot = refFuturesCurveSpot(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            likelyHoodRatio = zeros(NMC,1);
            transitionProbRef = zeros(NMC,1);
            transitionProb = zeros(NMC,1);
            % we generate conditional probability matrix first
            volProxyRefYN = 'NO';
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            if strcmp(eqCOMDupireSpotGF.modelParams('ApplyLikelyHoodRatioYN'),'YES')
                volProxyRefYN = 'YES';
            else
                % apply lastXIdxRef as lastXIdx & 
                % lastXWeightRef as lastXWeight
                
                volProxyRefYN = 'NO';
                lastXIdxRef = lastXIdx;
                lastXWeightRef = lastXWeight;
            end
            condProbRef = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime,volProxyRefYN);
            
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            QaRef = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbRef,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nextXIdxRef   = zeros(NMC,1);
            nextXWeightRef = zeros(NMC,1);
            
            indexMc2= 0;
            indexMc2Ref= 0;
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                indexMcRef = lastXIdxRef(i);
                cumProb1 = Qa(indexMc,:);
                cumProb1Ref = QaRef(indexMcRef,:);
                
                condProb1 = condProb(indexMc,:);
                condProb1Ref = condProbRef(indexMcRef,:);
                
                if indexMc > 1
                    indexMc2 = indexMc-1;
                else
                    indexMc2 = indexMc;
                end
                cumProb2 = Qa(indexMc2,:);
                
                if indexMcRef > 1
                    indexMc2Ref = indexMcRef-1;
                else
                    indexMc2Ref = indexMcRef;
                end
                cumProb2Ref = QaRef(indexMc2Ref,:);
                
                condProb2 = condProb(indexMc2,:);
                condProb2Ref = condProbRef(indexMc2Ref,:);
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                cumProbRef = (1.0-lastXWeightRef(i))*cumProb1Ref + lastXWeightRef(i)*cumProb2Ref;
                
                idxH1 = min(find(uSample(i) < cumProb));
                idxH1Ref = min(find(uSample(i) < cumProbRef));
                
                nextXIdx(i) = idxH1;
                nextXIdxRef(i) = idxH1Ref;

                weightedCondProb = (1.0-lastXWeight(i))*condProb1(idxH1) + lastXWeight(i)*condProb2(idxH1);
                weightedCondProbLikely = (1.0-lastXWeight(i))*condProb1(idxH1Ref) + lastXWeight(i)*condProb2(idxH1Ref);
                
                weightedCondProbRef = (1.0-lastXWeightRef(i))*condProb1Ref(idxH1Ref) + lastXWeightRef(i)*condProb2Ref(idxH1Ref);
                
                likelyHoodRatio(i) =    weightedCondProbLikely/weightedCondProbRef;  
            end
           
%            %% renormalize Radon Nikodym Derivatives 
%             if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                 avgLHR = mean(likelyHoodRatio);
%                 likelyHoodRatio = likelyHoodRatio/avgLHR;
%             end
            out.likelyHoodRatio = likelyHoodRatio;
          %% after calculating likelyHoodRatio
          %% we set nextIdx & nextXWeight as nextXIdxRef & nextXWeightRef 
            %% so that we follow the same trajectory (but with different probability weight)
            out.nextXIdx = nextXIdxRef;
            out.nextXWeight = nextXWeightRef;
            %% importtant correction above
            
            out.nextXIdxRef = nextXIdxRef;
            out.nextXWeightRef = nextXWeightRef;
            
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatioRef = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               dividendRatio = refFuturesValueSpot(nextFuturesIdx)/refFuturesValueSpot(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   
                 %% dividendRatioRef start
                   if nextXIdxRef(i) ==1 
                       nextXRef = Ks(nextXIdxRef(i));
                   else
                       nextXRef = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextXRef = nextXRef*(1.0 + dividendRatioRef);
                   idxDummyRef = find(nextXRef < Ks);
                   if isempty(idxDummyRef)
                       idxDummySRef = length(Ks);
                       weightRef = 0.0;
                   else
                       idxDummySRef = min(idxDummyRef);
                       if idxDummySRef == 1
                           weightRef = 0.0;
                       else
                           weightRef = (Ks(idxDummySRef) - nextXRef)/dK;
                       end
                   end

                   out.nextXIdxRef(i) = idxDummySRef;
                   out.nextXWeightRef(i) = weightRef;
                 
                 %% dividendRatioRef end
                 
                   if nextXIdxRef(i) ==1 
                       nextX = Ks(nextXIdxRef(i));
                   else
                       nextX = (1.0-nextXWeightRef(i))*Ks(nextXIdxRef(i)) + nextXWeightRef(i)*Ks(nextXIdxRef(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == length(Ks) || idxH1 == 0
                    nextXWeight(i) = 0.0;
                else
                    upperZ = norminv(cumProb(idxH1));
                    lowerZ = norminv(cumProb(idxH1-1));
                    sampleZ = norminv(uSample(i));
                    nextXWeight(i) = (upperZ -sampleZ)/(upperZ-lowerZ);
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyP)
                       predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            if strcmp(params.params.volProxyRefYN,'YES')
                settleFutures = eqCOMDupireSpotGF.settleFuturesRef;
            else
                settleFutures = eqCOMDupireSpotGF.settleFutures;
            end
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            cValue = fwdPriceCNew;
            pValue = fwdPricePNew;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffLikely(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
            cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
            if idx ~= 1 
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                        cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*cumulativeLikelyHoodRatio(idx11)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                    end
                end
              
                
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*cumulativeLikelyHoodRatio(idx11);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
                
            end    
            
            
        end
      
        function columnOut = MCPayoffLikelyRen(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            columnOut.cumLHR = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            columnOut.cumLHR = columnIn.cumLHR;
            
           %% cumulativeLikelyHoodRatio is given by the previous period's cumLHR and periodLikelyHoodRatio
           %% for alive path
           %% sum(cumLHR2) = N - sum(cumLHR1); 
            cumulativeLikelyHoodRatio = zeros(modelStatesSize,1);
            
            dumMeasureSum = 0.0;
            dumMeasureSumPrev = 0.0;
            dumMeasureN = 0;
            if idx == 1 
                cumulativeLikelyHoodRatio = periodLikelyHoodRatio;
                dumMeasureSum = sum(cumulativeLikelyHoodRatio);
                cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/dumMeasureSum*modelStatesSize;
                columnOut.cumLHR(:,idx) = cumulativeLikelyHoodRatio;
            else
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % dead path
                        dumMeasureSumPrev = dumMeasureSumPrev + columnIn.cumLHR(idx11,idx-1);
                        dumMeasureN = dumMeasureN + 1;
                    end
                end
                
                if dumMeasureN < modelStatesSize % if alive path normalize the relative measure
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = columnIn.cumLHR(idx11,idx-1)*periodLikelyHoodRatio(idx11);
                            dumMeasureSum = dumMeasureSum + cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                    
                    for idx11 =1:modelStatesSize
                        if columnOut.isStop(idx11,idx-1) ~= 1 % alive path
                            cumulativeLikelyHoodRatio(idx11) = cumulativeLikelyHoodRatio(idx11)/(dumMeasureSum)*(modelStatesSize - dumMeasureSumPrev);
                            columnOut.cumLHR(idx11,idx) = cumulativeLikelyHoodRatio(idx11);
                        end
                    end
                end
            end
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                
                for idx11 =1:modelStatesSize % 1st early redemption
                        % every path is an alive path use all path to
                       
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                     
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                end
                
                
            elseif idx > 1 && idx < scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                     
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*columnOut.cumLHR(idx11,idx)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                    end
                end
              
            else % idx == scheduleSize
                
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.cumLHR(idx11,idx) = columnOut.cumLHR(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                    
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % likelyhoodRatio operation
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*columnOut.cumLHR(idx11,idx);
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
   
                
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
         %% we delete roll overDates after maturity Date
           timeStep = timeStep(timeStep <= maturity);
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
            idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           cumLHR = ones(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);

%             periodLikelyHoodRatio = ones(modelStatesSize,1);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
              %% we generate cumulativeLikelyHoodRatio( for given period) starting from 1
              %% cumulativeLikelyHoodRatio : one period( between two cashflows) LHR
                periodLikelyHoodRatio = ones(modelStatesSize,1);
                for idx= startTimeIdx:1:endTimeIdx
                    
                   mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                nextXIdx,nextXWeight,U(:,idx));

%                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));

                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    periodLikelyHoodRatio = periodLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    
%                     if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
%                         avgLHR = mean(cumulativeLikelyHoodRatio);
%                         cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio/avgLHR;
%                     end
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    if strcmp(eqCOMDupireSpotGF.modelParams('ApplyLikelyHoodRatioYN'),'YES')
                        comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
                    else
                        comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    end
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.cumLHR = cumLHR;
                
                columnIn.payoffColumn = unhitValue;

%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                if strcmp(eqCOMDupireSpotGF.modelParams('renormalizeLHR'),'YES')
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikelyRen(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                else
                    columnOut = eqCOMDupireSpotGF.MCPayoffLikely(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn,periodLikelyHoodRatio);
                end
                
                
                
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                cumLHR = columnOut.cumLHR;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           out.forwardUnhitValue = unhitValue;
           out.forwardUnhitValue_npv = mean(unhitValue.payoff);
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                            %LHR measure change onto original
                            contiValue(idx) = contiValue(idx)/cumLHR(idx,i-1);
                            
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                                % No LikelyHoodRatio Correction
                                exerciseValue(idx) = exerciseValue(idx) * 1.0;
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                            unhitValue.payoff(idx) = unhitValue.payoff(idx)*cumLHR(idx,i-1);
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture;
           cumLHR_avg = mean(columnOut.cumLHR);
           out.cumLHR_last = cumLHR_avg(end);
           
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx+1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx+1);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                
%                 Z= randn(NMC/2,MCTimeStep);
%                 Z=[Z;-Z];
                
                Z= rand(NMC/2,MCTimeStep);
                %ANTITHETIC FOR UNIFORM RANDOM
                Z=[Z;1.0-Z];
                
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
%                 U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
           initXRef = ones(NMC,1)*S0Ref;
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1);
           
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           idxDummyRef = find(S0Ref < Ks);
           if isempty(idxDummyRef)
               error('S0Ref is not covered in the grid K')
           end
            
           idxDummySRef = min(idxDummyRef);
           weightRef = (Ks(idxDummySRef) - S0Ref)/dK;
           initXIdxRef = ones(NMC,1)*idxDummySRef;
           initXWeightRef = ones(NMC,1)*weightRef;
           
           
           nextX = initX;
           nextXRef = initXRef;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
           
           nextXIdxRef = initXIdxRef;
           nextXWeightRef =  initXWeightRef;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           cumulativeLikelyHoodRatio = ones(modelStatesSize,1);
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    
                        mcmcOut   = inductMCMCForwardLikely(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdxRef,nextXWeightRef,...
                                    nextXIdx,nextXWeight,U(:,idx));
%                         mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    nextXIdxRef = mcmcOut.nextXIdxRef;
                    nextXWeightRef = mcmcOut.nextXWeightRef;
                    
                    cumulativeLikelyHoodRatio = cumulativeLikelyHoodRatio.* mcmcOut.likelyHoodRatio;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           if strcmp(eqCOMDupireSpotGF.modelParams('ApplyLikelyHoodRatioYN'),'YES')
               comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdxRef,nextXWeightRef);
           else
               comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           end
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           %% likelyHoodRatio Calc
           for i=1:modelStatesSize
                payoffStateA.cashflow(i) = payoffStateA.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateB.cashflow(i) = payoffStateB.cashflow(i)*cumulativeLikelyHoodRatio(i);
                payoffStateC.cashflow(i) =  payoffStateC.cashflow(i)*cumulativeLikelyHoodRatio(i);
           end
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)

            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
           fwdPriceC = optParams.lastPriceC;
           fwdPriceP = optParams.lastPriceP;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdPriceC,fwdPriceP,optParams);
           
           fwdPriceCNew = out.fwdPriceCOut;
           fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,optParams); 
           
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           if strcmp(optParams.params.volProxyRefYN,'YES')
                blackOTMPrices = optParams.params.blackOTMPricesRef;
           else
               blackOTMPrices = optParams.params.blackOTMPrices;
           end
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastPriceC,lastPriceP,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastPriceC = lastPriceC;
            optParams.lastPriceP = lastPriceP;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastPriceC,lastPriceP,optParams);
            
            bootStrapOut.lastPriceC = out.fwdPriceCOut;
            bootStrapOut.lastPriceP = out.fwdPricePOut;
            
        end
        
        
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            
            blackOTMPricesRef = zeros(expirySize,strikeSize);
            fwdMoneynessRef = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end
            
            if  strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                settleFuturesRef = eqCOMDupireSpotGF.modelParams('settleFuturesRef');
                eqCOMDupireSpotGF.settleFuturesRef = settleFuturesRef;
                
                for k=1:expirySize
                    fwd = settleFuturesRef(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneynessRef(k,j) = strike(j)/fwd;
                        marketStrikesRef(k,j) = strike(j);
                        
                        if fwdMoneynessRef(k,j) <= 1.0
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPricesRef(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneynessRef(k,j),blackVol(k,j),'C');
                        end
                        
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackOTMPricesRef = blackOTMPricesRef;
            
            params.blackVol = blackVol;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            
            params.fwdMoneynessRef = fwdMoneynessRef;
            
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            idxDummy = find(S0 >= params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end
            
            idxDummyS = max(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (S0 - params.Ks(idxDummyS))/params.dK;
            
          %% Ref Curve update
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            
            idxDummyRef = find(S0Ref >= params.Ks);
            if isempty(idxDummyRef)
                error('S0Ref is not covered in the grid K')
            end
            
            idxDummySRef = max(idxDummyRef);
            params.PricingidxRef = idxDummySRef;
            params.PricingWeightRef = (S0Ref - params.Ks(idxDummySRef))/params.dK;
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            
            out.fwdMoneynessRef = fwdMoneynessRef;
            
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyRef = zeros(params.expirySize,params.strikeSize);
            
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR') ...
                    || strcmp(volSurface.params('moneyNessType'),'fixedStrikeLikely')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            initPriceCRef = zeros(params.Ns,1);
            initPricePRef = zeros(params.Ns,1);
            
            S0Ref = eqCOMDupireSpotGF.FwdNMRef(0);
            for idxh=1:params.Ns
                initPriceCRef(idxh) = max(S0Ref-params.Ks(idxh),0.0);
                initPricePRef(idxh) = max(-S0Ref+params.Ks(idxh),0.0);
            end
            
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPricesRef = blackOTMPricesRef;
            
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.modelImpVolRef  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.interpBlackPricesRef = zeros(expirySize,strikeSize);
            out.dupireOTMPricesRef = zeros(expirySize,strikeSize);
            out.dupireBlackVolRef = zeros(expirySize,strikeSize);
            out.volErrorRef = zeros(expirySize,strikeSize);
            out.priceReRef = zeros(expirySize,strikeSize);
            out.priceReOrigRef = zeros(expirySize,strikeSize);
            out.marketStrikesRef = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.PricingidxRef = params.PricingidxRef;
            out.PricingWeightRef = params.PricingWeightRef;
            out.nIterRef = zeros(expirySize,1);
            out.localVolRef = zeros(expirySize,length(out.Ks));
            out.rmseTotalRef=0.0;
            out.fwdVolMseTotalRef = 0.0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
            case 'bootstrapLikely'
                    
                %% calibrate to reference forward Curve start
%                    
                    %vol proxy calibration
                    
                    params.volProxyRefYN = 'YES';
                    
                    lastPriceCRef = initPriceCRef;
                    lastPricePRef = initPricePRef;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceCRef,lastPricePRef,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrigRef(i,j) = bootStrapOut.volProxy(j);
                            out.volProxyRef(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.iposRef(i,j)     = bootStrapOut.ipos(j);
                            out.volErrorRef(i,j) = bootStrapOut.volError(j);
                            out.marketImpVolRef(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVolRef(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPricesRef(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPricesRef(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceReRef(i,j) = out.dupireOTMPricesRef(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrigRef(i,j) = out.dupireOTMPricesRef(i,j)/out.blackOTMPricesRef(i,j)-1.0;
                            out.marketStrikesRef(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIterRef(i) = bootStrapOut.nIter;
                        tempLocalVolRef = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVolRef(i,j) = tempLocalVolRef(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceCRef = bootStrapOut.lastPriceC;
                        lastPricePRef = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotalRef = out.rmseTotalRef + out.priceReOrigRef(j,k)*out.priceReOrigRef(j,k);
                                out.fwdVolMseTotalRef = out.fwdVolMseTotalRef + out.volErrorRef(j,k)*out.volErrorRef(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotalRef = sqrt(out.rmseTotalRef/N);
                    out.fwdVolMseTotalRef = sqrt(out.fwdVolMseTotalRef/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxyRef = out.volProxyRef;
                    eqCOMDupireSpotGF.localVolSurface.iposRef = out.iposRef;
                    eqCOMDupireSpotGF.localVolSurface.localVolRef = out.localVolRef;
                    eqCOMDupireSpotGF.localVolSurface.PricingidxRef = out.PricingidxRef;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeightRef = out.PricingWeightRef;
%                     eqCOMDupireSpotGF.localVolSurface.probMeshRef = out.probMeshRef;
%                     eqCOMDupireSpotGF.localVolSurface.condProbRef = out.condProbRef;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
%                     eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
%                     eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
%                     eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
%                     eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
%                     eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    
                 %% calibrate to spot forward curve end
                    
                 %% calibrate to spot forward curve start
                    params.volProxyRefYN = 'NO';
                    
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.PricingWeight = out.PricingWeight;
%                     eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
%                     eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                  %% calibrate to spot forward curve end        
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFNMF < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        marketStrikes
        numOfFactors
        
        slope
        
       %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice

        targetStrikes
        
        %fixedStrike    
        settleFutures
        deltaH
        useYN
        deltaCutOff
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFNMF(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                %% SSR
                eqCOMDupireSpotGF.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqCOMDupireSpotGF.slope = EQModel.modelParams('slope');
                else
                    eqCOMDupireSpotGF.slope = 0.0;
                end
                
              %% SSR modelparams end
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
              %% SSR
                eqCOMDupireSpotGF.targetStrikes = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;

                %fixedStrike
                eqCOMDupireSpotGF.deltaCutOff = 0;
                eqCOMDupireSpotGF.useYN = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            for i=1:length(volProxy)
                volProxyKs(i) = eqCOMDupireSpotGF.marketStrikes(idxNow,i);
            end

            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),3);
                end

            else
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end
            end
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function out = BootStrapGFForward(eqCOMDupireSpotGF,tvar,fromTime,toTime,fwdPriceC,fwdPRiceP,optParams)
            
            %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           Ks = optParams.Ks;
           dK = optParams.dK;
           priceC = fwdPriceC;
           priceP = fwdPRiceP;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               outGF = eqCOMDupireSpotGF.BootStrapGFForwardOneStep(tvar,startTime,endTime,dK,...
                                        priceC,priceP,optParams);

               priceC = outGF.newPriceC;
               priceP = outGF.newPriceP;
               
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = priceC;
                   dummyP = priceP;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                       priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                       priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                       priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);
                       
                       if priceC(idxzz) < 0
                            priceC(idxzz) = 0.0;
                       end
                       
                       if priceP(idxzz) < 0
                           priceP(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           out.fwdPriceCOut = priceC;
           out.fwdPricePOut = priceP;
           
        end
        
        
        function out = BootStrapGFForwardOneStep(eqCOMDupireSpotGF,tvar,fromTime,toTime,dK,priceC,priceP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(priceC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            dT = (toTime-fromTime)/365.0;
            
            size = length(priceC);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newPriceC = A_exp1*priceC;
                newPriceP = A_exp1*priceP;
            
            end
            
            out.newPriceC = newPriceC;
            out.newPriceP = newPriceP;
            
%             out.condProb = condProb;
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
             %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMax = max(find(refFuturesExpiry < fromTime));
           idxRollMin = min(find(refFuturesExpiry >= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           volExpiry = eqCOMDupireSpotGF.localVolSurface.expiry;
           
           idxVolExpiryMax = max(find(volExpiry < fromTime));
           idxVolExpiryMin = min(find(volExpiry > toTime));
           idxVolExpiry = idxVolExpiryMin:1:idxVolExpiryMax;
           volExpiryTimes = volExpiry(idxVolExpiry);
           
           timeStep1 = sort(union(rollTimes,volExpiryTimes),'ascend');
           timeStep = sort(union(timeStep1,[fromTime,toTime]),'ascend');
           
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1);
           lastPrice = lastP;
          %% Solve  Backward PDE(GF)
           for idxh=length(timeStep):-1:2
               startTime = timeStep(idxh);
               endTime = timeStep(idxh-1);
               newPrice = eqCOMDupireSpotGF.inductGFBackwardOneTime(startTime,endTime,lastPrice);

               lastPrice = newPrice;
               
               idxhh = find(rollTimes == timeStep(idxh-1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyC = lastPrice;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyC)
                       NGP = floor( (Ks(idxzz)*(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                       if NGP < 1
                           NGP = 1;
                       end
                       
                       if NGP > length(dummyC)-1
                           NGP = length(dummyC)-1;
                       end
                       
                       weight = (Ks(idxzz)*(1.0 + dividendRatio)-Ks(NGP))/dK;
                       lastPrice(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                       
                       if lastPrice(idxzz) < 0
                            lastPrice(idxzz) = 0.0;
                       end
                   end
               end
           end
           
           newP = lastPrice;
            
        end
        
        function newP = inductGFBackwardOneTime(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end

        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1));
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
%             localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
%             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            
            marketStrikesPerExpiry = eqCOMDupireSpotGF.marketStrikes(idxNow,:);
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                dummyOut = interp1FlatExtrapNew(marketStrikesPerExpiry,volProxy,x','linear');
                localVol = dummyOut';
                
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                dummyOut = interp1FlatExtrapNew(marketStrikesPerExpiry,volProxy,x','pchip');
                localVol = dummyOut';
            else
                dummyOut = interp1FlatExtrapNew(marketStrikesPerExpiry,volProxy,x','linear');
                localVol = dummyOut';
            end
                
%             for ii =1:length(x)
%                 localVol(ii) = H_interpolation(Ks,localVolLine',x(ii),1);
%             end
            
        end
        
        function out = inductMCMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,...
                        lastProb,lastPriceC, lastPriceP,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            
            nextProb = lastProb*condProb;
            nextPriceC = condProb*lastPriceC;
            % Check the ex-dividend date & if it is then adjust prob accordingly 
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               dummyProb = nextProb;
               dummyC = nextPriceC; 
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;

               if dividendRatio > 0
                   
               end
               for  idxzz= 1:length(dummyProb)
                   NGP = floor( (Ks(idxzz)/(1.0 + dividendRatio) - Ks(1))/dK) + 1;
                   if NGP < 1
                       NGP = 1;
                   end

                   if NGP > length(dummyC)-1
                       NGP = length(dummyC)-1;
                   end

                   weight = (Ks(idxzz)/(1.0 + dividendRatio)-Ks(NGP))/dK;
                   priceC(idxzz) = (1.0-weight)*dummyC(NGP)+weight*dummyC(NGP+1);
                   priceC(idxzz) = (1.0 + dividendRatio)*priceC(idxzz);
                   priceP(idxzz) = (1.0-weight)*dummyP(NGP)+weight*dummyP(NGP+1);
                   priceP(idxzz) = (1.0 + dividendRatio)*priceP(idxzz);

                   if priceC(idxzz) < 0
                        priceC(idxzz) = 0.0;
                   end

                   if priceP(idxzz) < 0
                       priceP(idxzz) = 0.0;
                   end

               end
            end
            
            
            Qa = eqCOMDupireSpotGF.generateMarginalCumPerExpiry(nextProb,Ks);
            
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            nPoints = length(Ks);
            
            debugDx = zeros(NMC,1);
            debugIdx1 = zeros(NMC,1);
            debugIdx2 = zeros(NMC,1);
            debugWeight1 = zeros(NMC,1);
            debugWeight2 = zeros(NMC,1);
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                
                idxH1 = min(find(uSample(i) < cumProb1));
                idxH2 = min(find(uSample(i) < cumProb2));
                debugDx(i) = idxH1-idxH2;
                debugIdx1(i) = idxH1;
                debugIdx2(i) = idxH2;
                
                nextX = (1.0-lastXWeight(i))*Ks(idxH1) + lastXWeight(i)*Ks(idxH2);
                idxDummy = find(nextX < Ks);
                if isempty(idxDummy)
                    error('nextX is not covered in the grid K')
                end
                
                idxDummyS = min(idxDummy);
                weight = (Ks(idxDummyS)-nextX)/dK;
                nextXIdx(i) = idxDummyS;
                nextXWeight(i) = weight;
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;

            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                nextXIdx(i) = idxH1;
%                 if idxH1 > 1
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -cumProb(idxH1-1));
%                 else
%                     nextXWeight(i) = (cumProb(idxH1) -uSample(i))/(cumProb(idxH1) -0.0);
%                 end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastXIdx,lastXWeight,U)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
          %% find the futures roll overDates between fromTime to toTime end
           
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            dK = Ks(2) - Ks(1);
            NMC = length(lastXIdx);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            uSample = U;
            
            nextXIdx   = zeros(NMC,1);
            nextXWeight = zeros(NMC,1);
            
            
            for i=1:NMC
                indexMc = lastXIdx(i);
                cumProb1 = Qa(indexMc,:);
                if indexMc > 1
                    cumProb2 = Qa(indexMc-1,:);
                else
                    cumProb2 = Qa(indexMc,:);
                end
                cumProb = (1.0-lastXWeight(i))*cumProb1 + lastXWeight(i)*cumProb2;
                idxH1 = min(find(uSample(i) < cumProb));
                
                if length(idxH1) ~= 1
                    aaa = 1.0;
                end
                nextXIdx(i) = idxH1;
                
                if idxH1 == length(Ks) || idxH1 == 0
                    nextXWeight(i) = 0.0;
                else
                    upperZ = norminv(cumProb(idxH1));
                    lowerZ = norminv(cumProb(idxH1-1));
                    sampleZ = norminv(uSample(i));
                    nextXWeight(i) = (upperZ -sampleZ)/(upperZ-lowerZ);
                end
            end
            
            out.nextXIdx = nextXIdx;
            out.nextXWeight = nextXWeight;
            
            idxhh = find(rollTimes == toTime);
            
            % apply roll condition
            % interpolate along K dimension
            if ~isempty(idxhh)
               currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
               nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
               if isempty(nextFuturesIdxDummy)
                   error('there is not enough futures to roll!!');
               else
                   nextFuturesIdx = min(nextFuturesIdxDummy);
               end
               
               dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
               
               for i=1:NMC
                   if nextXIdx(i) ==1 
                       nextX = Ks(nextXIdx(i));
                   else
                       nextX = (1.0-nextXWeight(i))*Ks(nextXIdx(i)) + nextXWeight(i)*Ks(nextXIdx(i)-1);
                   end
                   nextX = nextX*(1.0 + dividendRatio);
                   idxDummy = find(nextX < Ks);
                   if isempty(idxDummy)
                       idxDummyS = length(Ks);
                       weight = 0.0;
                   else
                       idxDummyS = min(idxDummy);
                       if idxDummyS == 1
                           weight = 0.0;
                       else
                           weight = (Ks(idxDummyS) - nextX)/dK;
                       end
                   end

                   out.nextXIdx(i) = idxDummyS;
                   out.nextXWeight(i) = weight;
                   
               end
                
            end
            
        end
        
        
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function out = inductMCForwardNMF(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
          %% find the futures roll overDates between fromTime to toTime;
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           refFuturesExpiry = refFuturesCurve(:,1);
           refFuturesValue = refFuturesCurve(:,2);
           
           idxRollMin = min(find(refFuturesExpiry > fromTime));
           idxRollMax = max(find(refFuturesExpiry <= toTime));
           idxRoll = idxRollMin:1:idxRollMax;
           
           rollTimes = refFuturesExpiry(idxRoll);
           
           if length(rollTimes) > 1
                error('wrong timeSteps');
           end
           
           if length(rollTimes) == 1
                if rollTimes(1) ~= toTime
                    error('wrong timeSteps rolTimes(1) should be equal to toTime');
                end
           end
           
           
           timeStep = sort(union(rollTimes,[fromTime,toTime]),'ascend');
           
           predictor = lastX;
          %% Solve  Forward PDE(GF)
           for idxh=1:length(timeStep)-1
               startTime = timeStep(idxh);
               endTime = timeStep(idxh+1);
               corrector = eqCOMDupireSpotGF.inductMCForwardOneStep(startTime,endTime,predictor,dZ);
               predictor = corrector; 
               idxhh = find(rollTimes == timeStep(idxh+1));
               
               % apply roll condition
               % interpolate along K dimension
               if ~isempty(idxhh)
                   dummyP = predictor;
                   currentFuturesIdx = find(refFuturesExpiry ==rollTimes(idxhh));
                   nextFuturesIdxDummy = find(refFuturesExpiry > rollTimes(idxhh));
                   if isempty(nextFuturesIdxDummy)
                       error('there is not enough futures to roll!!');
                   else
                       nextFuturesIdx = min(nextFuturesIdxDummy);
                   end
                   dividendRatio = refFuturesValue(nextFuturesIdx)/refFuturesValue(currentFuturesIdx) - 1.0;
                   
                   for  idxzz= 1:length(dummyP)
                       predictor(idxzz) = dummyP(idxzz)*(1.0 + dividendRatio);
                   end
               end
           end
           
           out.nextX = predictor;
           
        end
        
        function mcmcOut = inductMCForwardOneStep(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNewPC(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            previousState = lastX;
            %lookup issue add small epsilon to fromTime
            volBegin = eqCOMDupireSpotGF.InterpolateLocalVol(previousState,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            predictor = previousState.*exp(-0.5.*volBegin.*volBegin*Dt + 1.0.*volBegin.*sqrtDt.*dZ); 
            
%             for i=1:length(lastX)
%                 predictor(i) = predictor(i)*exp(-0.5*volBegin(i)*volBegin(i)*Dt + volBegin(i)*sqrtDt*dZ(i)); 
%             end
            
            volEnd = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,toTime - 0.01);
            corrector = previousState.*exp(-0.5.*0.5.*volBegin.*volBegin*Dt-0.5.*0.5.*volEnd.*volEnd*Dt ...
                        + 1.0.*volBegin.*sqrtDt.*dZ); 
            
            mcmcOut.nextX = corrector;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,params)
            
            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            
            settleFutures = eqCOMDupireSpotGF.settleFutures;
            
            forward = settleFutures(idxNow);
            
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            cValue = fwdPriceCNew;
            pValue = fwdPricePNew;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                
                if K <= forward
                     marKetPrice = (1.0 - params.iweight(i))*pValue(params.ipos(i)) + params.iweight(i)*pValue(params.ipos(i)+1); 
                     out.vols(i) = blackVolLBR(marKetPrice,forward,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = marKetPrice;
                     out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    marKetPrice = (1.0 - params.iweight(i))*cValue(params.ipos(i)) + params.iweight(i)*cValue(params.ipos(i)+1); 
                    out.vols(i) = blackVolLBR(marKetPrice,forward,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = marKetPrice;
                    out.interpBlackPrices(i) = blackPrice(forward,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            idxNow = min(find(expiry <= maturity));
            fwd = eqCOMDupireSpotGF.settleFutures(idxNow);
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= fwd
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end
                
                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                newP = inductGFBackward(eqCOMDupireSpotGF,maturity,0,mesh);
                
                out = (1.0 - params.PricingWeight)*newP(params.Pricingidx)+params.PricingWeight*newP(params.Pricingidx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOneOld(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            stateSize = length(modelStates);
            
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end

        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
% %             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
%             forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             forwardCurveSize = size(forwardCurve,1);
%             forwardMaturity = forwardCurve(:,1); 
%             idx = find(observeTime <= forwardMaturity);
%              if isempty(idx)
%                 idxNM = forwardCurveSize;
%              else
%                 idxNM = min(idx);
%              end
%              
%              %fwd(0,T_NM)
%              fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
%              for i=1:stateSize
%                 stochasticFwd(i) = fwd_NM * modelStates(i); 
%              end
             
             for i=1:stateSize
                stochasticFwd(i) = modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMCMC(eqCOMDupireSpotGF,observeTime,modelStatesIdx,modelStatesWeight)

             stateSize = length(modelStatesIdx);
             stochasticFwd = zeros(stateSize,1);
             Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
             
             for i=1:stateSize
                idx = modelStatesIdx(i);
                weight = modelStatesWeight(i);
                
                if idx == 1
                    stochasticFwd(i)= Ks(idx);
                else
                    stochasticFwd(i) =(1.0 - weight)*Ks(idx) + weight*Ks(idx-1);
                end
                 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           % current spot on the grid
           % nearest month forward at t=0
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCPC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNewPC(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            eqCOMDupireSpotGF.localVolSurface.volProxy = ones(size(fwdMoneyness))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMCNMF(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           initProb = zeros(1,gridSize);
           initProb(idxDummyS) = 1.0-weight;
           initProb(idxDummyS-1) = weight;
           
           initPriceC = zeros(length(Ks),1);
           initPriceP = zeros(length(Ks),1);
            
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           for idxh=1:length(Ks)
               initPriceC(idxh) = max(S0-Ks(idxh),0.0);
               initPriceP(idxh) = max(-S0+Ks(idxh),0.0);
           end
           
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           nextProb = initProb;
           nextPriceC = initPriceC;
           nextPriceP = initPriceP;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),...
%                                 nextXIdx,nextXWeight,nextProb,nextPriceC,nextPriceP,U(:,idx));
                            
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                            
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             

        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
             if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
             end
             
        %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
%             useQuasiRandomYN = 'true';
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                 
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
                U = H_ncdf(U);

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
%            initX = ones(NMC,1);
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           nextX = initX;
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           hitValue.npv = (1.0-PricingWeight)*hitValue.payoff(Pricingidx)+ PricingWeight*hitValue.payoff(Pricingidx+1);
           unhitValue.npv = (1.0-PricingWeight)*unhitValue.payoff(Pricingidx)+ PricingWeight*unhitValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+PricingWeight*nMFuture.payoff(Pricingidx+1);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           dummyVar = 0;
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            dummyMeshB = zeros(length(timeStep),2);
%            dummyIdx = 1;
%            dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
%            dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%            dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
%                     %apply american option
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
%                     onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
%                     contiValueB  = meshB/onePayoffD;
%                     
%                     payoffStateB.cashflow = zeros(modelStatesSize,1);
%                     payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
%                     if strcmp(vanillaParams.params('callPutFlag'),'C')
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
%                             if payoffStateB.cashflow(j) > contiValueB(j)
%                                 ccc = 1.0;
%                             end
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                         
%                     else
%                         for j=1:modelStatesSize
%                             payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
%                             payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
%                         end
%                     end
%                     payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
%                     meshB = payoffStateB.cashflow_npv;
%                     dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
%                     dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
%                     dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           PricingWeight = eqCOMDupireSpotGF.localVolSurface.PricingWeight;
           
           europeanValue.npv = (1.0-PricingWeight)*europeanValue.payoff(Pricingidx) + PricingWeight*europeanValue.payoff(Pricingidx+1);
           americanValue.npv = (1.0-PricingWeight)*americanValue.payoff(Pricingidx)+ PricingWeight*americanValue.payoff(Pricingidx+1);
           nMFuture.npv = (1.0-PricingWeight)*nMFuture.payoff(Pricingidx)+ PricingWeight*nMFuture.payoff(Pricingidx+1);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNMF(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMCMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            
            %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep = sort(union(timeStep,rollTimes),'ascend');
           
           timeStep = timeStep(timeStep <= maturity);
           
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'YES')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);
                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
               
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                U = H_ncdf(U);
            end
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           S0 = eqCOMDupireSpotGF.FwdNM(0);
           initX = ones(NMC,1)*S0;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           gridSize = length(Ks);
           dK = Ks(2) - Ks(1); 
           idxDummy = find(S0 < Ks);
           if isempty(idxDummy)
               error('S0 is not covered in the grid K')
           end
            
           idxDummyS = min(idxDummy);
           weight = (Ks(idxDummyS) - S0)/dK;
           initXIdx = ones(NMC,1)*idxDummyS;
           initXWeight = ones(NMC,1)*weight;
           
           nextX = initX;
           
           nextXIdx = initXIdx;
           nextXWeight =  initXWeight;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
%                     mcmcOut   = inductMCMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextXIdx,nextXWeight,U(:,idx));
                    
                    nextXIdx = mcmcOut.nextXIdx;
                    nextXWeight = mcmcOut.nextXWeight;
                    
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMCMC(currentTime,nextXIdx,nextXWeight);
           
           if isKey(vanillaParams.params,'digitalYN')
               if strcmp(vanillaParams.params('digitalYN'),'YES')
                   digitalCoupon = vanillaParams.params('digitalCoupon'); 
                   if strcmp(vanillaParams.params('callPutFlag'),'C')
                       for i=1:modelStatesSize
                           if (comFwd(i) >= strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   else
                       for i=1:modelStatesSize
                           if (comFwd(i) <  strike) dummyVar = 1.0;else dummyVar = 0.0;end;
                            payoffStateA.cashflow(i) = digitalCoupon*dummyVar;
                            payoffStateB.cashflow(i) = digitalCoupon*dummyVar;
                       end
                   end
               end
                   
               
           else
               if strcmp(vanillaParams.params('callPutFlag'),'C')
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                        payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
                   end
               else
                   for i=1:modelStatesSize
                        payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                        payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
                   end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            initX = ones(NMC,1)*S0;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            idxh = find(timeScheduleInfo.timeSchedule <= maturity);
            timeStep = timeScheduleInfo.timeSchedule(idxh);
            timeStep = sort(timeStep,'ascend');
            
%            %% find the futures roll overDates
%             refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
%             rollTimes = refFuturesCurve(:,1);
%            
%             timeStep = sort(union(timeStep1,rollTimes),'ascend');
%             timeStep = timeStep(timeStep <= maturity);
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                out = eqCOMDupireSpotGF.inductMCForwardNMF(timeStep(i-1),timeStep(i),nextX,dZStep);
                nextX = out.nextX;
            end
            
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            dK = Ks(2) - Ks(1);
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            idxDummy = find(S0 < Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end

            idxDummyS = min(idxDummy);
            weight = (Ks(idxDummyS) - S0)/dK;
            initXIdx = ones(NMC,1)*idxDummyS;
            initXWeight = ones(NMC,1)*weight;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            %% find the futures roll overDates
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(timeStep,rollTimes),'ascend');
            
            idxh = find(timeStep1 <= maturity);
            timeStep = timeStep1(idxh);
            timeStep = sort(timeStep,'ascend');
            
            nextXIdx = initXIdx;
            nextXWeight = initXWeight;
            
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextXIdx,nextXWeight,U(:,i-1));
                nextXIdx = mcmcOut.nextXIdx;
                nextXWeight = mcmcOut.nextXWeight;
            end
            
            nextX = eqCOMDupireSpotGF.CommoFwdNMMCMC(expiry,nextXIdx,nextXWeight);
            idxh = find(expiry == maturity);
            forward = eqCOMDupireSpotGF.settleFutures(idxh);
            for j=1:length(strikes)
                if(strikes(j) <= forward)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
          %% find the futures roll overDates
           refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
           rollTimes = refFuturesCurve(:,1);
           
           timeStep1 = sort(union(volExpiry,rollTimes),'ascend');
            
            newTimeSchedule = sort(union(timeStep1,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
%             MCTimeStep = length(expiry); % -1 because 0
            
            refFuturesCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            rollTimes = refFuturesCurve(:,1);
           
            timeStep1 = sort(union(expiry,rollTimes),'ascend');
            MCTimeStep = length(timeStep1);
            
            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        function out = generateMarginalCumPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(1,length(Ks));
            cumM = 0;
            Qa(1) = condProb(1);
            for j=2:nPoints
                cumM = cumM + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
           idxNow = optParams.idxNow;
           fromTime= optParams.fromTime;
           toTime = optParams.toTime;
            
%            induct priceC, priceP forward
           fwdPriceC = optParams.lastPriceC;
           fwdPriceP = optParams.lastPriceP;
            
           out = eqCOMDupireSpotGF.BootStrapGFForward(tvar,fromTime,toTime,fwdPriceC,fwdPriceP,optParams);
           
           fwdPriceCNew = out.fwdPriceCOut;
           fwdPricePNew = out.fwdPricePOut;
           
           target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,fwdPriceCNew,fwdPricePNew,optParams); 
           
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,fromTime,toTime,lastPriceC,lastPriceP,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = (toTime-fromTime)/365.0;
            optParams.fromTime = fromTime;
            optParams.toTime = toTime;
            
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.iweight = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
                
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.marketStrikes(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
                optParams.iweight(i) = (optParams.marketStrikes(i) - optParams.Ks(optParams.ipos(i)))/optParams.dK;
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastPriceC = lastPriceC;
            optParams.lastPriceP = lastPriceP;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;

            % fixedStrikeTest
            if eqCOMDupireSpotGF.deltaCutOff > 0
                useYN = eqCOMDupireSpotGF.useYN(idxNow,:);
                if idxNow <= numOfCutoffTenor
                    lowerIdx = min(find(useYN > 0));
                    upperIdx = max(find(useYN > 0));
                end
            end

            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
%             out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            out = eqCOMDupireSpotGF.BootStrapGFForward(bootStrapOut.volProxy,fromTime,toTime,lastPriceC,lastPriceP,optParams);
            
            bootStrapOut.lastPriceC = out.fwdPriceCOut;
            bootStrapOut.lastPriceP = out.fwdPricePOut;
            
        end
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            deltaH = zeros(expirySize,strikeSize);
            

            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            %% useYN is a static variables for fixedStrike calibration
            % if moneynessType is fixedStrike then useYN is meaningful
            % otherwise it is id matrix
            
            eqCOMDupireSpotGF.useYN = eqCOMDupireSpotGF.modelParams('useYN');
            eqCOMDupireSpotGF.deltaCutOff = eqCOMDupireSpotGF.modelParams('deltaCutOff');
            
            if strcmp(volSurface.params('moneyNessType'),'fixedStrike')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFuturesSpot');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                
                for k=1:expirySize
                    fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        marketStrikes(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = fwd*BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                   end
                end
                
            
            end

%             eqCOMDupireSpotGF.useYN = useYN;
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
          %% Due to SSR we change initial localVol
            
            
            params.fwdMoneyness = fwdMoneyness;
            params.marketStrikes = marketStrikes;
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            eqCOMDupireSpotGF.marketStrikes = marketStrikes;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            % nearest month forward at t=0
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            
            idxDummy = find(S0 >= params.Ks);
            if isempty(idxDummy)
                error('S0 is not covered in the grid K')
            end
            
            idxDummyS = max(idxDummy);
            params.Pricingidx = idxDummyS;
            params.PricingWeight = (S0 - params.Ks(idxDummyS))/params.dK;
            
%             params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            out.useYN = ones(params.expirySize,params.strikeSize);

            if strcmp(volSurface.params('moneyNessType'),'fixedStrike') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR')
                out.useYN = eqCOMDupireSpotGF.useYN;
            end

            %initialze the intial probability distribution in the grid
            %initialze the intial option price on the grid
            
            initPriceC = zeros(params.Ns,1);
            initPriceP = zeros(params.Ns,1);
            
            S0 = eqCOMDupireSpotGF.FwdNM(0);
            for idxh=1:params.Ns
                initPriceC(idxh) = max(S0-params.Ks(idxh),0.0);
                initPriceP(idxh) = max(-S0+params.Ks(idxh),0.0);
            end
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.PricingWeight = params.PricingWeight;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;

            out.rmseTotal1 = 0;
            out.fwdVolMseTotal1 = 0;

            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastPriceC = initPriceC;
                    lastPriceP = initPriceP;
                    
                    for i=1:expirySize
                        if  i ~= 1
                            fromTime = params.expiry(i-1);
                            toTime   = params.expiry(i);
                        else
                            fromTime = 0;
                            toTime = params.expiry(1);
                        end
                        
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,fromTime,toTime,lastPriceC,lastPriceP,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
%                             out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
%                         out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastPriceC = bootStrapOut.lastPriceC;
                        lastPriceP = bootStrapOut.lastPriceP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            if eqCOMDupireSpotGF.useYN(j,k) > 0
                                out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                                out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                                N=N+1;
                            end
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
%                     params.marketStrikes = out.marketStrikes;
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <= fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        settleFutures = eqCOMDupireSpotGF.settleFutures;
                        for i=1:expirySize
                            fwd = settleFutures(i);
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=fwd
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),fwd,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        useYN = eqCOMDupireSpotGF.useYN;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if useYN(j,k) > 0
                                    out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                    out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end
                    
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFMR < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        numOfFactors
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFMR(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            try
                fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            catch ME
                aaa = 0;
            end
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    aaa =1.0;
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end   
                
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function out = Solve1DGFMR(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            MRGridInfo = optParams.params.MRGridInfo;
            Ks = MRGridInfo.MRGrid{optParams.idxNow};
            
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                error('Not Supported GFType!')
%                 oneStepDt = optParams.params.oneStepDt;
%                 NT = round(dT/oneStepDt);
%                 
%                 A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
%                 A_exp1 = expm(A_rg);
%                 
%                 newProb = lastProb;
%                 condProb = eye(size,size);
%                 for t=1:NT
%                     newProb = newProb*A_exp1;
%                     condProb = A_exp1*A_exp1;
%                 end
                
            elseif optParams.params.GFType == 3
                error('Not Supported GFType!')
%                 a1 = a(2:size);
%                 c1 = c(1:size-1);
%             
%                 % Test for HugeDecomposition for inverse matrix
%                 [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
%                 A = gallery('tridiag',a1,b,c1);
%                 oneStep = OneStepGF(size,x,y,d,A);
%                 newProb = lastProb;
%                 newProb = newProb*oneStep;
%                 
%                 condProb = oneStep;
                
            else
                error('Not Supported GFType!')
%                 oneStepDt = optParams.params.oneStepDt;
%                 NT = round(dT/oneStepDt);
%                 
%                 % rescale matrix element to smaller time step
%                 a= a*oneStepDt/dT;
%                 b = (b-1)*oneStepDt/dT + 1.0;
%                 c = c*oneStepDt/dT;
%                 
%                 a1 = a(2:size);
%                 c1 = c(1:size-1);
%             
%                 % Test for HugeDecomposition for inverse matrix
%                 [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
%                 A = gallery('tridiag',a1,b,c1);
%                 oneStep = OneStepGF(size,x,y,d,A);
%                 newProb = lastProb;
%                 %numberOfTimeStep;
%                 %oneStepDt = 1.0/365;
%                 
%                 condProb = eye(size,size);
%                 for t=1:NT
%                     newProb = newProb*oneStep;
%                     condProb = oneStep*oneStep;
%                 end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function out = Solve1DGFMR_expmv(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            MRGridInfo = optParams.params.MRGridInfo;
            Ks = MRGridInfo.MRGrid{optParams.idxNow};
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            
            newProbT = expmv(dT,A_rg',lastProb');
            out.newProb = newProbT';
            out.condProb = 0.0;
            
%             A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%             newProb = lastProb*A_exp1;
            

        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1));
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            % we use the same linear interpolation scheme as calibration
            useVolProxyInterpolationYN = 'YES';
            if strcmp(useVolProxyInterpolationYN,'YES')
                
                for ii =1:length(x)
                    localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
                end
            else
                volKnotPoints = zeros(length(ipos),1);
                for i=1: length(ipos)
                    volKnotPoints(i) = Ks(ipos(i));
                end


                for i=1:length(x)
                    xIdx = find(volKnotPoints <=x(i));
                    if isempty(xIdx)
                        localVol(i) = localVolLine(1);
                    elseif max(xIdx) == ipos(length(ipos))
                        localVol(i) = localVolLine(length(ipos));
                    else
                        localVolIdx = max(xIdx);
                        weight = (x(i)-Ks(ipos(localVolIdx)))/(Ks(ipos(localVolIdx)+1)-Ks(ipos(localVolIdx)));
                        localVol(i) = weight*localVolLine(ipos(localVolIdx)+1)+(1-weight)*localVolLine(ipos(localVolIdx));
                    end
                end
            end
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U,Ks)
            
            NMC = length(lastX);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U)
            
            NMC = length(lastX);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = InterpolateTargetStrikeVolFPIMR(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
%             modelX = params.Ks;
            modelX = params.params.MRGridInfo.MRGrid{idxNow};
            
            modelXSize = length(modelX);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotGenericMC(eqCOMDupireSpotGF,valueDate,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            if observeTime < 0
                allFixings = eqCOMDupireSpotGF.modelParams('allFixings');
                fixingDate = AddDate(valueDate,observeTime,'day');
                equity1Fixings = allFixings('Equity1Index');
                try
                    fixing = equity1Fixings(StrDate(fixingDate,'str'));
                    stateSize = length(modelStates);
                    out = ones(stateSize,1)*fixing;
                    
                catch exception
                    throw(exception)
                end
            else
                spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
                detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

                 %stochasticFwd(0,T)
                 stateSize = length(modelStates);
                 stochasticFwd = zeros(stateSize,1);

                 for i=1:stateSize
                    stochasticFwd(i) = detFwd * modelStates(i); 
                 end

                 out = stochasticFwd;
            end
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeConvertibleBond1SMCEQ(eqCOMDupireSpotGF,valueDate,convertibleBondParams)
%           
            % model schedule generation
            
            %% couponSchedule start
            
            couponScheduleInt = convertibleBondParams.params.couponInfo.couponScheduleInt;
            
            % schedule is couponSchedule
            % main backbone schedule
            scheduleSize = size(couponScheduleInt,1);
            couponSchedule= struct;
            % coupon payment event happens at endDate
            %eventTime is endDate
            % payment date can be different from endDate
            for i=1:scheduleSize
%                 couponSchedule.payDate(i) = H_Date(couponScheduleInt(i,4));
                couponStartDate = H_Date(couponScheduleInt(i,2));
                couponEndDate = H_Date(couponScheduleInt(i,3));
                couponPayDate = H_Date(couponScheduleInt(i,4));
                
                couponSchedule.dayCount(i) = couponEndDate.DateDiff(couponStartDate);
                couponSchedule.dayCountFraction(i) = couponSchedule.dayCount(i)/365.0; 
                
                couponSchedule.eventTime(i) = DateDiff(couponEndDate,valueDate);
                couponSchedule.payTime(i) = DateDiff(couponPayDate,valueDate);
                
%                 couponSchedule.strike(i) = scheduleInt(i,2);
%                 couponSchedule.coupon(i) = scheduleInt(i,3);
            end
            couponSchedule.scheduleSize = scheduleSize;
            
%             expiryDate = couponSchedule.payDate(scheduleSize);
            expiryDate = convertibleBondParams.endDate;
            
            %% coupon schedule end
            
            %% puttable schedule start
            %% put exercise event happens the same date of payment
            puttableScheduleInt = convertibleBondParams.params.puttableInfo.puttableScheduleInt;
            puttableScheduleSize = size(puttableScheduleInt,1);
            puttableSchedule= struct;
            for i=1:puttableScheduleSize
                putExerciseDate = H_Date(puttableScheduleInt(i,1));
                
                puttableSchedule.eventTime(i) = DateDiff(putExerciseDate,valueDate);
                puttableSchedule.payTime(i) = DateDiff(putExerciseDate,valueDate);
                puttableSchedule.putPayment(i) = puttableScheduleInt(i,2);
            end
            puttableSchedule.scheduleSize = puttableScheduleSize;
            
           %% puttable schedule end
           
            %% call exercise event happens the same date of payment
            %% callable schedule start
            callableScheduleInt = convertibleBondParams.params.callableInfo.callableScheduleInt;
            callableScheduleSize = size(callableScheduleInt,1);
            callableSchedule= struct;
            for i=1:callableScheduleSize
                callExerciseDate = H_Date(callableScheduleInt(i,1));
                callableSchedule.eventTime(i) = DateDiff(callExerciseDate,valueDate);
                callableSchedule.payTime(i) = DateDiff(callExerciseDate,valueDate);
                
                 callableSchedule.callPayment(i) = callableScheduleInt(i,2);
            end
            callableSchedule.scheduleSize = callableScheduleSize;
            % condition on stockprice such that callable condition is
            % triggered
            callableConditionalStrike = convertibleBondParams.params.callableInfo.callableConditionalStrike;
            
           %% callable schedule end
           
           %% convertible info start
            
           %% refixing schedule start
            refixingScheduleInt = convertibleBondParams.params.convertibleInfo.refixingScheduleInt;
            refixingScheduleSize = size(refixingScheduleInt,1);
            refixingSchedule= struct;
            for i=1:refixingScheduleSize
                fixing1MStartDate = H_Date(refixingScheduleInt(i,1));
                fixing1WStartDate = H_Date(refixingScheduleInt(i,2));
                fixing1DStartDate = H_Date(refixingScheduleInt(i,3));
                refixingDate = H_Date(refixingScheduleInt(i,4));
                
                refixingSchedule.fixing1MStartEventTime(i) = DateDiff(fixing1MStartDate,valueDate);
                refixingSchedule.fixing1WStartEventTime(i) = DateDiff(fixing1WStartDate,valueDate);
                refixingSchedule.fixing1DStartEventTime(i) = DateDiff(fixing1DStartDate,valueDate);
                
                refixingSchedule.eventTime(i) = DateDiff(refixingDate,valueDate);
                refixingSchedule.payTime(i) = DateDiff(refixingDate,valueDate);
%                 refixingSchedule.payTime(i) = DateDiff(refixingDate,valueDate); 
            end
            refixingSchedule.scheduleSize = refixingScheduleSize;
            
            
          %% refixing schedule end
                %% convertible info
            initialConversionStrike = convertibleBondParams.params.convertibleInfo.conversionStrike;
            refixingStrikeGlobalFloor = convertibleBondParams.params.convertibleInfo.refixingStrikeGlobalFloor;
          %% convertible info end
            
            
          %% pricing time Step Generation start
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            
            aliveCoupon = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            eventTimeStep = volExpiry;
            if strcmp(eqCOMDupireSpotGF.modelParams('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                eventTimeStep = sort(union(eventTimeStep,dailyTimeSteps),'ascend');
            else
                error('for convertible bond we only use daily time steps!')
%                 timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
%                 dailyTimeSteps = [maturity:-timeStepP:0]';
%                 dailyTimeSteps = [dailyTimeSteps;0];
%                 timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
%             % we include couponPayDatees
%             expiredCoupon = 0;
%             aliveCoupon = 0;
%             for i= 1:scheduleSize
%                 daysToCoupon = couponSchedule.days(i);
%                 if daysToCoupon <= 0
%                     expiredCoupon = expiredCoupon +1;
%                     continue;
%                 else
%                     aliveCoupon = aliveCoupon + 1;
% %                     timeStep = [timeStep; daysToCoupon];
%                 end 
%             end
%             
%             lastAliveCouponIdx = 1 + expiredCoupon;
%             
%             % we include puttable schedule
%             expiredPut = 0;
%             alivePut = 0;
%             for i= 1:puttableScheduleSize
%                 daysToPut = puttableSchedule.days(i);
%                 if daysToPut <= 0
%                     expiredPut = expiredPut +1;
%                     continue;
%                 else
%                     alivePut = alivePut + 1;
% %                     timeStep = [timeStep; daysToPut];
%                 end 
%             end
%             
%             lastAlivePutIdx = 1 + expiredPut;
%             
%             % we include callable schedule
%             expiredCall = 0;
%             aliveCall = 0;
%             for i= 1:callableScheduleSize
%                 daysToCall = callableSchedule.days(i);
%                 if daysToCall <= 0
%                     expiredCall = expiredCall +1;
%                     continue;
%                 else
%                     aliveCall = aliveCall + 1;
% %                     timeStep = [timeStep; daysToCall];
%                 end 
%             end
%             lastAliveCallIdx = 1 + expiredCall;
%             % we include convertible schedule? no
%             % we just check whether we are in ther convertible possible period
%             
%             % we include refixing date
            
            
            eventTimeStep = sort(union(eventTimeStep,maturity),'ascend');
            
            aliveTimeStep = eventTimeStep(eventTimeStep>=0);
            aliveTimeStep = sort(aliveTimeStep,'ascend');
            
            totalAliveTimeStepSize = length(aliveTimeStep);
            
            % should we use eventTimeIdx as future only time stes?
            % In this case we better use more generic approach
            % such time all times steps are included 
            % and when payoff description is decoded, time should be
            % checked later
            
            
%             eventTimeIdx = zeros(couponSchedule.scheduleSize,1);
%             
%             for i= couponSchedule.scheduleSize:-1:lastAliveCouponIdx
%                 idx = find(timeStep == couponSchedule.days(i));
%                 eventTimeIdx(i) = min(idx);
%             end
           
          %% pricing time Step Generation end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalAliveTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalAliveTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = convertibleBondParams.params.nominal;
           basePrice = convertibleBondParams.params.basePrice;
           coupon = convertibleBondParams.params.couponInfo.coupon;
%            lowerBarrier = convertibleBondParams.params('lowerBarrier');
%            overHedgeShift = convertibleBondParams.params('overHedgeShift');
%            overHedgeSpread = convertibleBondParams.params('overHedgeSpread');
%            
%            callStrike1 = convertibleBondParams.params('callStrike1');
%            callValue1 = convertibleBondParams.params('callValue1');
%            SSpayoffYN = convertibleBondParams.params('SSpayoffYN');
%            KIYN = convertibleBondParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.initialConversionStrike = initialConversionStrike;
           payoffInfo.refixingStrikeGlobalFloor = refixingStrikeGlobalFloor;
%            payoffInfo.overHedgeSpread = overHedgeSpread;
%            
%            payoffInfo.callStrike1 = callStrike1;
%            payoffInfo.callValue1 = callValue1;
%            payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.couponSchedule = couponSchedule;
           payoffInfo.puttableSchedule = puttableSchedule;
           payoffInfo.callableSchedule = callableSchedule;
           payoffInfo.refixingSchedule = refixingSchedule;
           
           
           modelStatesSize = NMC;
           
          %% Define Pricing Columns
           % we need avg1MStockPrice, avg1WStockPrice,avg1DStockPrice,
           % floatingConversionStrike  <- all can be treated as
           % stateVariable
           
           % for the cashflow generated pricing columns as pricerInfo
           % we do not use pricerInfo Structure but simplified ones
           
          %% state variable initialize
%            worstP          = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           avg1MStockPrice = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           avg1WStockPrice = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           avg1DStockPrice = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           floatingConversionStrike = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           
           stateVariables = containers.Map({'avg1MStockPrice','avg1WStockPrice'}, ...
                        {avg1MStockPrice,avg1WStockPrice});
                    
           stateVariables('avg1DStockPrice') = avg1DStockPrice;
           stateVariables('floatingConversionStrike') = floatingConversionStrike;
           
          %% PricingColumns that has cashflows
           % we have fixedCouponBond, convertibleOnlyBond,
           % puttableOnlyBond, convertibleAndPuttableBond,
           % convertiblePuttableCallableBond
                      
           %fixedCouponBond 
           fixedCouponBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %convertibleOnlyBond
           convertibleOnlyBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %puttableOnlyBond
           puttableOnlyBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %convertibleAndPuttableBond
           convertibleAndPuttableBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %convertiblePuttableCallableBond
           convertiblePuttableCallableBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %convertiblePuttableCallableBond
           convertibleOnlyBond = PricerInfoSimple(modelStatesSize,scheduleSize);
            %dummy floatingStrikeC
           floatingStrikeC= PricerInfoSimple(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use accruedSumOfStockPrice for moving average calculation 
           accruedSum1M = zeros(modelStatesSize,1);
           accruedSum1W = zeros(modelStatesSize,1);
           accruedSum1D = zeros(modelStatesSize,1);
           
           accruedDays1M = 0;
           accruedDays1W = 0;
           accruedDays1D = 0;
           
           previousConversionStrike = initialConversionStrike*ones(modelStatesSize,1);
           
            % we use all path for regression
            % conversion ITM , puttable ITM ,  callable ITM
            % what's the use of Alive Path only Regression Sampling ?
            
%            isStop = zeros(modelStatesSize,scheduleSize);
%            worstP = zeros(modelStatesSize,scheduleSize);
           
           
           % check whether current future price breach the barrier
%            comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
           comFwd = eqCOMDupireSpotGF.EQSpotGenericMC(valueDate,currentTime,nextX);
           
%           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
          %% Path Generation Forward
          %% Store (state) variables to be used for AMC Regression
           currentCouponPeriod = 1;
           %payoff descrption update index
           currentTimeIdx = 1;
           %MC numMethodState update index
           aliveTimeIdx = 1;
           % currentTimeStep is update in for statement
%            for currentTimeStep = eventTimeStep(1):1:eventTimeStep(end)
           for idxT = 1:1:length(eventTimeStep)
                currentTimeStep = eventTimeStep(idxT);
                % evaluate scripts 
                % evaluate stateVariables(stores)
                % evaluate expression per each pricing columns
                % at the end of the loop we induct forward
                % from left to right
                % fictional payoff script columns are
                % avg1MStockPrice,avg1WStockPrice,
                % avg1DStockPrice,floatingConversionStrke
                % worstP,fixedCouponBond,....
                
                % just evaluate spotPrice for the use in;
                comFwd = eqCOMDupireSpotGF.EQSpotGenericMC(valueDate,currentTimeStep,nextX);
                        
                % find the current
                % if find return errors then?
                try
                    % find the corresponding nearest future refixing event
                    idx = min(find(currentTimeStep <= refixingSchedule.eventTime));
                    
                  %% stateVariable avg1MStockPrice,avg1WStockPrice,avg1DStockPrice
                  %% floatingConversionStrike
                  
                    % if avg1MStockPrice evaluate condition is met
                    if currentTimeStep >= refixingSchedule.fixing1MStartEventTime(idx) ...
                       && currentTimeStep < refixingSchedule.eventTime(idx)
                   
                        accruedSum1M  = accruedSum1M + comFwd;
                        accruedDays1M = accruedDays1M +1;
                    end
                    
                    % if avg1WStockPrice evaluate condition is met
                    if currentTimeStep >= refixingSchedule.fixing1WStartEventTime(idx) ...
                       && currentTimeStep < refixingSchedule.eventTime(idx)
                   
                        accruedSum1W  = accruedSum1W + comFwd;
                        accruedDays1W = accruedDays1W +1;
                    end
                    
                    % if avg1DStockPrice evaluate condition is met
                    
                    if currentTimeStep >= refixingSchedule.fixing1DStartEventTime(idx) ...
                       && currentTimeStep < refixingSchedule.eventTime(idx)
                   
                        accruedSum1D  = accruedSum1D + comFwd;
                        accruedDays1D = accruedDays1D +1;
                    end
                    
                    % now if we are at refixingSchedule eventTime
                    % (refixingDate)
                    % fixingEventTime(idx)
                    % update floatingConversionStrike
                    if currentTimeStep == refixingSchedule.eventTime(idx)
                        
                        avg1MStockPrice(:,idx) =  accruedSum1M(:)/accruedDays1M;
                        avg1WStockPrice(:,idx) =  accruedSum1W(:)/accruedDays1W;
                        avg1DStockPrice(:,idx) =  accruedSum1D(:)/accruedDays1D;
                        
                        % save floatingConversionStrike per path, and
                        % update previousConversionStrike for the future
                        % use
                        for idx2=1:modelStatesSize
                            
                            floatingConversionStrike(idx2,idx) = min(previousConversionStrike(idx2,1),...
                                max(avg1MStockPrice(idx2,idx),avg1WStockPrice(idx2,idx),avg1DStockPrice(idx2,idx)));
                            
                            previousConversionStrike(idx2,1) = floatingConversionStrike(idx2,idx);
                        end
                        
                    end
                    
                 %% PricingColumns1: fixedCouponBond
                   idxCoupon = min(find(currentTimeStep <= couponSchedule.eventTime));
                   % if currentTime  is couponSchedule.eventTime
                  
                   if currentTimeStep == couponSchedule.eventTime(idxCoupon)
                        %fixedCouponCashflow
                         dcf = couponSchedule.dayCountFraction(idxCoupon);
                         payoffStateA.cashflow = nominal*coupon*dcf*ones(modelStatesSize,1);
                         df_e = 1.0;
                   end
                   
                    % if currentTimeSteps is today or future then inductMCForward
                    if currentTimeStep >= 0 && currentTimeStep < eventTimeStep(end)
                        nextTimeStep = eventTimeStep(currentTimeIdx +1);
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,currentTimeStep,nextTimeStep,nextX,U(:,aliveTimeIdx));
                        nextX = mcmcOut.nextX;
                        %MC numMethodState update
                        aliveTimeIdx = aliveTimeIdx + 1;
                    end
                    
                    currentTimeIdx = currentTimeIdx +1;
                catch exception
                    throw(exception)
                end
                
                
           end
           
           bbb = 1.0;
           
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCEQ(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        
        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 40000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = unhitValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           dummyMeshB = zeros(length(timeStep),2);
           dummyIdx = 1;
           dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
           dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
           dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                    %apply american option
                    comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValueB  = meshB/onePayoffD;
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    if strcmp(vanillaParams.params('callPutFlag'),'C')
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
                            if payoffStateB.cashflow(j) > contiValueB(j)
                                ccc = 1.0;
                            end
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                        
                    else
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                    end
                    payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
                    meshB = payoffStateB.cashflow_npv;
                    dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
                    dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
                    dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = europeanValue.payoff(Pricingidx);
           americanValue.npv = americanValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardStartingVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            startDate  = H_Date(vanillaParams.params('startDate'));
            
            scheduleSize = 2;
            % resetDate
            % expiryDate
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            daysToReset = DateDiff(startDate,valueDate);
            
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,daysToReset),'ascend');
            
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            
            eventTimeIdx(1) = find(timeStep == daysToReset);
            eventTimeIdx(2) = find(timeStep == maturity);
            
%             for i= scheduleSize:-1:lastAliveExerciseIdx
%                 idx = find(timeStep == maturity);
%                 eventTimeIdx(i) = min(idx);
%             end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           relativeStrike =  vanillaParams.params('relativeStrike');
           
           detFwdReset    = eqCOMDupireSpotGF.FwdFactor(daysToReset);
           detFwdMaturity = eqCOMDupireSpotGF.FwdFactor(maturity);
           
           fwdRatio = detFwdMaturity/detFwdReset;
           
%            relativeStrike =  [0.5:0.1:1.5];
           
           reSetS = zeros(NMC,1);      
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                if i== 1
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                else
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                end
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                % at startDate, we reset strike
                if i==1
                    comFwd = eqCOMDupireSpotGF.EQFwdMC(currentTime,nextX);
                    reSetS = comFwd;
                    
                end
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.EQFwdMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i)/reSetS(i) - relativeStrike*fwdRatio,0);
                    payoffStateB.cashflow(i) = max(comFwd(i)/reSetS(i) - relativeStrike*fwdRatio,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i)/reSetS(i) + relativeStrike*fwdRatio,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i)/reSetS(i) + relativeStrike*fwdRatio,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
%            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           df_ep = 1.0;
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture;
           out.fwdRatio = fwdRatio;
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            
            initX = ones(NMC,1);
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                nextX = eqCOMDupireSpotGF.inductMCForward(timeStep(i-1),timeStep(i),startIdx,endIdx,timeScheduleInfo,nextX,dZStep,params);
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            initX = ones(NMC,1);
            initXIdx = ones(NMC,1)*params.Pricingidx;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            nextXIdx = initXIdx;
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextX,nextXIdx,U(:,i-1),Ks);
                nextX = mcmcOut.nextX;
                nextXIdx = mcmcOut.nextXIdx;
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
            newTimeSchedule = sort(union(volExpiry,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
            MCTimeStep = length(expiry); % -1 because 0

            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            
            
          %% Solve  Forward PDE(GF) One time
            outGF = eqCOMDupireSpotGF.Solve1DGF(tvar,mkt_dT,optParams.dK,optParams.lastProb,optParams);
            
            newProb = outGF.newProb;
            optParams.meshProb = newProb;
           %% PDE(GF) Solve End
           % find the implied vol of dupire model
           if strcmp(eqCOMDupireSpotGF.modelParams('UseLetsBeRational'),'YES')
               target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           else
               target = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           end
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
        function  out  = TargetFunctionVolProxyFPIMR(eqCOMDupireSpotGF,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            
            
          %% Solve  Forward PDE(GF) One time
            dK = optParams.params.MRGridInfo.MRGridStep(idxNow);
%             outGF = eqCOMDupireSpotGF.Solve1DGF(tvar,mkt_dT,dK,optParams.lastProb,optParams);
            outGF = eqCOMDupireSpotGF.Solve1DGFMR(tvar,mkt_dT,dK,optParams.lastProb,optParams);
            
            newProb = outGF.newProb;
            optParams.meshProb = newProb;
           %% PDE(GF) Solve End
           % find the implied vol of dupire model
           if strcmp(eqCOMDupireSpotGF.modelParams('UseLetsBeRational'),'YES')
%                target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,newProb,optParams);
               target = InterpolateTargetStrikeVolFPIMR(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           else
               target = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           end
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
        function  out  = TargetFunctionVolProxyFPIMR_expmv(eqCOMDupireSpotGF,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            
            
          %% Solve  Forward PDE(GF) One time
            dK = optParams.params.MRGridInfo.MRGridStep(idxNow);
%             outGF = eqCOMDupireSpotGF.Solve1DGF(tvar,mkt_dT,dK,optParams.lastProb,optParams);

            if optParams.params.useExpMVFlag
                outGF = eqCOMDupireSpotGF.Solve1DGFMR_expmv(tvar,mkt_dT,dK,optParams.lastProb,optParams);
            else
                outGF = eqCOMDupireSpotGF.Solve1DGFMR(tvar,mkt_dT,dK,optParams.lastProb,optParams);
            end
            
            newProb = outGF.newProb;
            optParams.meshProb = newProb;
           %% PDE(GF) Solve End
           % find the implied vol of dupire model
           if strcmp(eqCOMDupireSpotGF.modelParams('UseLetsBeRational'),'YES')
%                target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,newProb,optParams);
               target = InterpolateTargetStrikeVolFPIMR(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           else
               target = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           end
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,dT,lastProb,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.fwdMoneyness(idxNow,i);
            end
                
%             if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
%                 % market strike points in fwd PDE grid
%                 fwdFactor = eqCOMDupireSpotGF.FwdFactor(params.expiry(idxNow));
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i)/fwdFactor;
%                 end
%             else
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i);
%                 end
%             end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastProb = lastProb;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;
            
            if idxNow <= numOfCutoffTenor
                lowerIdx = min(find(optParams.marketStrikes >= lowerCutoff));
                upperIdx = max(find(optParams.marketStrikes <= upperCutoff));
            end
            
            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

%             targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
%             targetfunc = @(tvar) TargetFunctionVolProxyFPIMR(eqCOMDupireSpotGF,tvar,optParams);
            targetfunc = @(tvar) TargetFunctionVolProxyFPIMR_expmv(eqCOMDupireSpotGF,tvar,optParams);
                
            
%             tol = 0.0001;
%             maxIter = 1000;
            
            tol = params.tol;
            maxIter = params.maxIter;
            tic
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            toc
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
            if optParams.params.useExpMVFlag
                out = eqCOMDupireSpotGF.Solve1DGFMR_expmv(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            else
                out = eqCOMDupireSpotGF.Solve1DGFMR(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            end
            
            bootStrapOut.lastProb = out.newProb;
            bootStrapOut.condProb = out.condProb;
            
        end
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            if strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess')
                for k=1:expirySize
    %                 fwd = black.Fwd(spot,expiry(k));
    %                 df = black.zeroCurve.DF(expiry(k)/365.0);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize

                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        if strike(j) <= 0
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        else
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        end

                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'P');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'C');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        end
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                         
                    end
                    dfOut(k) = black.zeroCurve.DF(expiry(k)/365.0);
                end
                
            end
                
%             if strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         fwdStrike = strike(j)/fwdFactor;
%                         if fwdStrike <= 1.0
% %                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                         else
% %                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                             blackOTMPrices(k,j)  = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                             
%                         end
%                     end
%                 end
%             else
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         if strike(j) <= 1
%                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                         else
%                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                         end
%                     end
%                 end
%             end
%             
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
            params.fwdMoneyness = fwdMoneyness;
            
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
          %% multiResolution Grid Generation Start
           % since gridStrip Size is different for each time interval
           % we generate targetGrid as cell structures
           atmVols = eqCOMDupireSpotGF.modelParams('atmVols');
           MRGridStep = eqCOMDupireSpotGF.modelParams('MRGridStep');
           MRStdNumbers = eqCOMDupireSpotGF.modelParams('MRStdNumbers');
           
           MRExpiry = atmVols(:,1);
           MRExpirySize = length(MRExpiry);
           MRGridSize = length(MRExpiry);
           MRGridMin = length(MRExpiry);
           MRGridMax = length(MRExpiry);
           
           MRGridInfo = struct;
           MRGrid = cell(MRExpirySize,1);
           pricingIdxMR = zeros(MRExpirySize,1);
           
           for idxJ=1:MRExpirySize
               
                gridStep = MRGridStep(idxJ);
                stdNumber = MRStdNumbers(idxJ);
                x_min = exp(-1.0*stdNumber*atmVols(idxJ,2)*sqrt(atmVols(idxJ,1)/365.0));
                x_max = exp(1.0*stdNumber*atmVols(idxJ,2)*sqrt(atmVols(idxJ,1)/365.0));
                atmXIdx = floor((1.0-x_min)/gridStep) + 1;
                pricingIdxMR(idxJ) = atmXIdx;
                gridSize = floor((x_max - x_min)/gridStep) + 1;
                MRGridGridStrip = zeros(gridSize,1);
                
                for idxY = 1:gridSize
                    MRGridGridStrip(idxY) = 1.0 + (idxY-atmXIdx)*gridStep;
                end
                
                MRGridMin(idxJ) = MRGridGridStrip(1);
                MRGridMax(idxJ) = MRGridGridStrip(end);
                
%                 if MRGridMin(idxJ) > params.Kmin
%                     x_min = 0.1;
%                     x_max = 2.5;
%                     atmXIdx = floor((1.0-x_min)/gridStep) + 1;
%                     pricingIdxMR(idxJ) = atmXIdx;
%                     gridSize = floor((x_max - x_min)/gridStep) + 1;
%                     MRGridGridStrip = zeros(gridSize,1);
%                     for idxY = 1:gridSize
%                         MRGridGridStrip(idxY) = 1.0 + (idxY-atmXIdx)*gridStep;
%                     end
% 
%                     MRGridMin(idxJ) = MRGridGridStrip(1);
%                     MRGridMax(idxJ) = MRGridGridStrip(end);
%                 end
                
                idxNeg = find(MRGridGridStrip <=0);
                if idxNeg
                    error('negative X is in the Grid!')
                end
                
                MRGrid{idxJ} = MRGridGridStrip;
                MRGridSize(idxJ) = gridSize;
           end
           
           MRGridInfo.MRGrid     = MRGrid;
           MRGridInfo.MRGridSize = MRGridSize;
           MRGridInfo.MRExpiry = MRExpiry;
           MRGridInfo.MRGridStep = MRGridStep;
           MRGridInfo.pricingIdxMR = pricingIdxMR;
           MRGridInfo.MRStdNumbers = MRStdNumbers;
           params.MRGridInfo = MRGridInfo;
           params.useExpMVFlag = eqCOMDupireSpotGF.modelParams('useExpMVFlag');
           
          %% multiResolution Grid Generation End 
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            
            %initialze the intial probability distribution in the grid
%             initProb = zeros(1,params.Ns);
%             initProb(params.Pricingidx) = 1.0;
            
            initProb = zeros(1,params.MRGridInfo.MRGridSize(1));
            initProb(params.MRGridInfo.pricingIdxMR(1)) = 1.0;
            
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;
            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
%                     toc
                    
%                     tic
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    params.marketStrikes = out.marketStrikes;
                    
%                     toc
                    
%                     calculate backward scheme for given target
%                     compareforwardMCFlag = 1 for one step euler scheme
%                     compareforwardMCFlag = 2 for daily euler scheme
%                     
%                     compareforwardMCFlag = 3 for markov chain monte carlo
                     
                    
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
  
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end

%                     toc
                case 'bootstrapForward'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    % compute implied surface for targetStrikes;
                    targetExpiry = params.expiry;
                    
                    %% at T call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVol = outDummy.impVolSurface;
                    out.cValueSurface = outDummy.cValueSurface;
                    out.pValueSurface = outDummy.pValueSurface;
                    out.probMeshInt = outDummy.probMeshInt;
                    
                     %% at T-dT call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0.000001;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVolPrev = outDummy.impVolSurface;
                    out.cValueSurfacePrev = outDummy.cValueSurface;
                    out.pValueSurfacePrev = outDummy.pValueSurface;
                    out.probMeshIntPrev = outDummy.probMeshInt;
                    
                    aaa = 1.0;
                    
                case 'bootstrapForwardOnly'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    aaa = 1.0;
                    
                    
                      

                otherwise
                    disp('unImplemented')
                    
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFMon < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        numOfFactors
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFMon(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
%                     eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')= 'matlabMonotonCubicSplineMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            try
                fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            catch ME
                aaa = 0;
            end
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    aaa =1.0;
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end   
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabMonotonCubicSplineMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                % monotonic cubic spline interpolation
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),3);
                end     
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1));
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            % we use the same linear interpolation scheme as calibration
            useVolProxyInterpolationYN = 'YES';
            if strcmp(useVolProxyInterpolationYN,'YES')
                if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabMonotonCubicSplineMarketFwdMoneyness')
                    for ii =1:length(x)
                        localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),3);
                    end
                elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabLinearMarketFwdMoneyness')
                    for ii =1:length(x)
                        localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
                    end
                else
                    for ii =1:length(x)
                        localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
                    end
                end
            else
                volKnotPoints = zeros(length(ipos),1);
                for i=1: length(ipos)
                    volKnotPoints(i) = Ks(ipos(i));
                end


                for i=1:length(x)
                    xIdx = find(volKnotPoints <=x(i));
                    if isempty(xIdx)
                        localVol(i) = localVolLine(1);
                    elseif max(xIdx) == ipos(length(ipos))
                        localVol(i) = localVolLine(length(ipos));
                    else
                        localVolIdx = max(xIdx);
                        weight = (x(i)-Ks(ipos(localVolIdx)))/(Ks(ipos(localVolIdx)+1)-Ks(ipos(localVolIdx)));
                        localVol(i) = weight*localVolLine(ipos(localVolIdx)+1)+(1-weight)*localVolLine(ipos(localVolIdx));
                    end
                end
            end
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U,Ks)
            
            NMC = length(lastX);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U)
            
            NMC = length(lastX);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 40000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = unhitValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           dummyMeshB = zeros(length(timeStep),2);
           dummyIdx = 1;
           dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
           dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
           dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                    %apply american option
                    comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValueB  = meshB/onePayoffD;
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    if strcmp(vanillaParams.params('callPutFlag'),'C')
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
                            if payoffStateB.cashflow(j) > contiValueB(j)
                                ccc = 1.0;
                            end
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                        
                    else
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                    end
                    payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
                    meshB = payoffStateB.cashflow_npv;
                    dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
                    dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
                    dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = europeanValue.payoff(Pricingidx);
           americanValue.npv = americanValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            
            initX = ones(NMC,1);
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                nextX = eqCOMDupireSpotGF.inductMCForward(timeStep(i-1),timeStep(i),startIdx,endIdx,timeScheduleInfo,nextX,dZStep,params);
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            initX = ones(NMC,1);
            initXIdx = ones(NMC,1)*params.Pricingidx;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            nextXIdx = initXIdx;
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextX,nextXIdx,U(:,i-1),Ks);
                nextX = mcmcOut.nextX;
                nextXIdx = mcmcOut.nextXIdx;
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
            newTimeSchedule = sort(union(volExpiry,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
            MCTimeStep = length(expiry); % -1 because 0

            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            
            
          %% Solve  Forward PDE(GF) One time
            outGF = eqCOMDupireSpotGF.Solve1DGF(tvar,mkt_dT,optParams.dK,optParams.lastProb,optParams);
            
            newProb = outGF.newProb;
            optParams.meshProb = newProb;
           %% PDE(GF) Solve End
           % find the implied vol of dupire model
           if strcmp(eqCOMDupireSpotGF.modelParams('UseLetsBeRational'),'YES')
               target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           else
               target = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           end
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,dT,lastProb,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.fwdMoneyness(idxNow,i);
            end
                
%             if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
%                 % market strike points in fwd PDE grid
%                 fwdFactor = eqCOMDupireSpotGF.FwdFactor(params.expiry(idxNow));
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i)/fwdFactor;
%                 end
%             else
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i);
%                 end
%             end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastProb = lastProb;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;
            
            if idxNow <= numOfCutoffTenor
                lowerIdx = min(find(optParams.marketStrikes >= lowerCutoff));
                upperIdx = max(find(optParams.marketStrikes <= upperCutoff));
            end
            
            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
%             tol = 0.0001;
%             maxIter = 1000;
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
            out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            bootStrapOut.lastProb = out.newProb;
            bootStrapOut.condProb = out.condProb;
            
        end
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            if strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess')
                for k=1:expirySize
    %                 fwd = black.Fwd(spot,expiry(k));
    %                 df = black.zeroCurve.DF(expiry(k)/365.0);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize

                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        if strike(j) <= 0
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        else
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        end

                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'P');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'C');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        end
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                         
                    end
                    dfOut(k) = black.zeroCurve.DF(expiry(k)/365.0);
                end
                
            end
                
%             if strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         fwdStrike = strike(j)/fwdFactor;
%                         if fwdStrike <= 1.0
% %                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                         else
% %                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                             blackOTMPrices(k,j)  = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                             
%                         end
%                     end
%                 end
%             else
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         if strike(j) <= 1
%                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                         else
%                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                         end
%                     end
%                 end
%             end
%             
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
            params.fwdMoneyness = fwdMoneyness;
            
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            
            %initialze the intial probability distribution in the grid
            initProb = zeros(1,params.Ns);
            initProb(params.Pricingidx) = 1.0;
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;
            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
%                     toc
                    
%                     tic
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    params.marketStrikes = out.marketStrikes;
                    
%                     toc
                    
%                     calculate backward scheme for given target
%                     compareforwardMCFlag = 1 for one step euler scheme
%                     compareforwardMCFlag = 2 for daily euler scheme
%                     
%                     compareforwardMCFlag = 3 for markov chain monte carlo
                     
                    
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
  
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end

%                     toc
                case 'bootstrapForward'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    % compute implied surface for targetStrikes;
                    targetExpiry = params.expiry;
                    
                    %% at T call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVol = outDummy.impVolSurface;
                    out.cValueSurface = outDummy.cValueSurface;
                    out.pValueSurface = outDummy.pValueSurface;
                    out.probMeshInt = outDummy.probMeshInt;
                    
                     %% at T-dT call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0.000001;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVolPrev = outDummy.impVolSurface;
                    out.cValueSurfacePrev = outDummy.cValueSurface;
                    out.pValueSurfacePrev = outDummy.pValueSurface;
                    out.probMeshIntPrev = outDummy.probMeshInt;
                    
                    aaa = 1.0;
                    
                case 'bootstrapForwardOnly'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    aaa = 1.0;
                    
                    
                      

                otherwise
                    disp('unImplemented')
                    
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFFixedStrike < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        numOfFactors
        
        %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice
        
        %fixedStrike
        settleFutures
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFFixedStrike(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
%                     eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')= 'matlabMonotonCubicSplineMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;
                
                eqCOMDupireSpotGF.pricingForwardGrid = [];
                eqCOMDupireSpotGF.pricingReducedForwardGrid = [];
                eqCOMDupireSpotGF.pricingVolGrid = [];
                eqCOMDupireSpotGF.volNodeFwdCurve = [];
                eqCOMDupireSpotGF.modelStatesFixedGrid = [];

            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            try
                fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            catch ME
                aaa = 0;
            end
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    aaa =1.0;
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end   
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabMonotonCubicSplineMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                % monotonic cubic spline interpolation
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),3);
                end     
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
          
        function localVol = GetLocalVolFromProxyFixedGrid(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow,ratio)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            try
                fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            catch ME
                aaa = 0;
            end
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    aaa =1.0;
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(Ks)
%                     localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                    localVol(i) = H_interpolation(volProxyKs,volProxy,ratio*Ks(i),1);
                end   
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabMonotonCubicSplineMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                % monotonic cubic spline interpolation
                for i=1:length(Ks)
%                     localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),3);
                    localVol(i) = H_interpolation(volProxyKs,volProxy,ratio*Ks(i),3);
                end     
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function newP = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP, basePrice)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
%             ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            ipos = 0;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
%             proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            
            fwdNM = eqCOMDupireSpotGF.FwdNM(fromTime);
            ratio = basePrice/fwdNM;
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxyFixedGrid(volProxy,Ks,ipos,idxNow,ratio);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function newP = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = log(Ks(2)/Ks(1));
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
            for i=1:size
                temp = 0.5*dT*proxy(i)*proxy(i)/dK;
                a(i) = -temp*(1.0/dK + 0.5);
                b(i) = 1 + 2.0/dK*temp;
                b_rg(i) = b(i) - 1.0;
                c(i) = -temp * (1.0/dK - 0.5);
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1));
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            % we use the same linear interpolation scheme as calibration
            useVolProxyInterpolationYN = 'YES';
            if strcmp(useVolProxyInterpolationYN,'YES')
                if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabMonotonCubicSplineMarketFwdMoneyness')
                    for ii =1:length(x)
                        localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),3);
                    end
                elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabLinearMarketFwdMoneyness')
                    for ii =1:length(x)
                        localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
                    end
                else
                    for ii =1:length(x)
                        localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
                    end
                end
            else
                volKnotPoints = zeros(length(ipos),1);
                for i=1: length(ipos)
                    volKnotPoints(i) = Ks(ipos(i));
                end


                for i=1:length(x)
                    xIdx = find(volKnotPoints <=x(i));
                    if isempty(xIdx)
                        localVol(i) = localVolLine(1);
                    elseif max(xIdx) == ipos(length(ipos))
                        localVol(i) = localVolLine(length(ipos));
                    else
                        localVolIdx = max(xIdx);
                        weight = (x(i)-Ks(ipos(localVolIdx)))/(Ks(ipos(localVolIdx)+1)-Ks(ipos(localVolIdx)));
                        localVol(i) = weight*localVolLine(ipos(localVolIdx)+1)+(1-weight)*localVolLine(ipos(localVolIdx));
                    end
                end
            end
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U,Ks)
            
            NMC = length(lastX);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U)
            
            NMC = length(lastX);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end

        function mcmcOut = inductMCForwardFineVolGrid(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime + 0.01);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
    
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);

            localVol = zeros(length(predictor),1);

            for ii=1:length(predictor)
                localVol(ii) = H_interpolation(Ks,proxy,predictor(ii),1);
            end

%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, ~,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNMFixedGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             
             volNodeFwdCurve = eqCOMDupireSpotGF.volNodeFwdCurve;
             
             volNodeFwdSize = size(volNodeFwdCurve,1);
             volNodeFwdMaturity = volNodeFwdCurve(:,1); 
             idxVol = find(observeTime <= volNodeFwdMaturity);
             if isempty(idxVol)
                idxVolNM = volNodeFwdSize;
             else
                idxVolNM = min(idxVol);
             end
             
             fwd_VolNM = volNodeFwdCurve(idxVolNM,2);
             basePrice = eqCOMDupireSpotGF.basePrice;
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM/fwd_VolNM * basePrice * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.25
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            eqCOMDupireSpotGF.localVolSurface.volProxy = ones(size(fwdMoneyness))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SMCFineVolGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;


            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    mcmcOut   = inductMCForwardFineVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 40000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*df_ep;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = meshC;
                
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    contiValueC = nMFuture.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = contiValueC;
                    
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*onePayoffD;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = unhitValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SGFFixedGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% fixedGrid generation start
            
            basePrice = stepdownParams.params('basePrice');
            
            %% PricingIdx & WeightNextPriceIndex update
           PricingIdx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           %nearest futures at evaluation
           fwdNM = eqCOMDupireSpotGF.FwdNM(0);
           spotLevel = fwdNM/basePrice;
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           %% fixedGrid fwd
           fwdNM = eqCOMDupireSpotGF.FwdNM(currentTime);
           comFwd = comFwd/fwdNM*basePrice;
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
                    meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                     %% fixedGrid fwd
                    fwdNM = eqCOMDupireSpotGF.FwdNM(currentTime);
                    comFwd = comFwd/fwdNM*basePrice;
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    %% fixedGrid fwd
                    fwdNM = eqCOMDupireSpotGF.FwdNM(currentTime);
                    comFwd = comFwd/fwdNM*basePrice;
                    
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SGFPricingVolGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            
            % grid size is log equi distant with 0.5% size
            dy = 0.005;
            volATM = impVolSurf(size(volProxy,1),round(size(volProxy,2)+1)/2);
            

%             X_max = max(1.3*fwdNM(size(volProxy,1)),basePrice*exp(5.0*volATM*sqrt(expiry(size(volProxy,1))/365.0)));
%             X_min = min(0.7*fwdNM(size(volProxy,1)),basePrice*exp(-5.0*volATM*sqrt(expiry(size(volProxy,1))/365.0)));
%             
            X_max = basePrice*exp(5.0*volATM*sqrt(expiry(size(volProxy,1))/365.0));
            X_min = basePrice*exp(-5.0*volATM*sqrt(expiry(size(volProxy,1))/365.0));
            
            K = round(log(X_max/X_min)/dy);
            temp_pricingForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingForwardGrid(i,j) = X_min*exp((j-1)*dy);
                      temp_pricingReducedForwardGrid(i,j) = temp_pricingForwardGrid(i,j)/fwdNM(i);
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid/basePrice;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
%            basePrice = stepdownParams.params('basePrice');
           
            %nearest futures at evaluation
           fwdNM  =  eqCOMDupireSpotGF.FwdNM(0);
           fwdVolNM = eqCOMDupireSpotGF.volNodeFwdCurve(1,2);
                   
           spotLevel = fwdVolNM/basePrice;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
                    mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           dummyMeshB = zeros(length(timeStep),2);
           dummyIdx = 1;
           dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
           dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
           dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                    %apply american option
                    comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValueB  = meshB/onePayoffD;
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    if strcmp(vanillaParams.params('callPutFlag'),'C')
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
                            if payoffStateB.cashflow(j) > contiValueB(j)
                                ccc = 1.0;
                            end
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                        
                    else
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                    end
                    payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
                    meshB = payoffStateB.cashflow_npv;
                    dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
                    dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
                    dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = europeanValue.payoff(Pricingidx);
           americanValue.npv = americanValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            
            initX = ones(NMC,1);
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                nextX = eqCOMDupireSpotGF.inductMCForward(timeStep(i-1),timeStep(i),startIdx,endIdx,timeScheduleInfo,nextX,dZStep,params);
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            initX = ones(NMC,1);
            initXIdx = ones(NMC,1)*params.Pricingidx;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            nextXIdx = initXIdx;
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextX,nextXIdx,U(:,i-1),Ks);
                nextX = mcmcOut.nextX;
                nextXIdx = mcmcOut.nextXIdx;
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
            newTimeSchedule = sort(union(volExpiry,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
            MCTimeStep = length(expiry); % -1 because 0

            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            
            
          %% Solve  Forward PDE(GF) One time
            outGF = eqCOMDupireSpotGF.Solve1DGF(tvar,mkt_dT,optParams.dK,optParams.lastProb,optParams);
            
            newProb = outGF.newProb;
            optParams.meshProb = newProb;
           %% PDE(GF) Solve End
           % find the implied vol of dupire model
           if strcmp(eqCOMDupireSpotGF.modelParams('UseLetsBeRational'),'YES')
               target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           else
               target = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           end
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,dT,lastProb,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.fwdMoneyness(idxNow,i);
            end
                
%             if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
%                 % market strike points in fwd PDE grid
%                 fwdFactor = eqCOMDupireSpotGF.FwdFactor(params.expiry(idxNow));
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i)/fwdFactor;
%                 end
%             else
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i);
%                 end
%             end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastProb = lastProb;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;
            
            if idxNow <= numOfCutoffTenor
                lowerIdx = min(find(optParams.marketStrikes >= lowerCutoff));
                upperIdx = max(find(optParams.marketStrikes <= upperCutoff));
            end
            
            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
%             tol = 0.0001;
%             maxIter = 1000;
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
            out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            bootStrapOut.lastProb = out.newProb;
            bootStrapOut.condProb = out.condProb;
            
        end
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            if strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess')
                for k=1:expirySize
    %                 fwd = black.Fwd(spot,expiry(k));
    %                 df = black.zeroCurve.DF(expiry(k)/365.0);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize

                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        if strike(j) <= 0
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        else
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        end

                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'P');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'C');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        end
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                         
                    end
                    dfOut(k) = black.zeroCurve.DF(expiry(k)/365.0);
                end
                
            end
                
%             if strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         fwdStrike = strike(j)/fwdFactor;
%                         if fwdStrike <= 1.0
% %                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                         else
% %                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                             blackOTMPrices(k,j)  = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                             
%                         end
%                     end
%                 end
%             else
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         if strike(j) <= 1
%                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                         else
%                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                         end
%                     end
%                 end
%             end
%             
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
            params.fwdMoneyness = fwdMoneyness;
            
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            
            %initialze the intial probability distribution in the grid
            initProb = zeros(1,params.Ns);
            initProb(params.Pricingidx) = 1.0;
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;
            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
%                     toc
                    
%                     tic
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    params.marketStrikes = out.marketStrikes;
                    
%                     toc
                    
%                     calculate backward scheme for given target
%                     compareforwardMCFlag = 1 for one step euler scheme
%                     compareforwardMCFlag = 2 for daily euler scheme
%                     
%                     compareforwardMCFlag = 3 for markov chain monte carlo
                     
                    
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
  
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end

%                     toc
                case 'bootstrapForward'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    % compute implied surface for targetStrikes;
                    targetExpiry = params.expiry;
                    
                    %% at T call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVol = outDummy.impVolSurface;
                    out.cValueSurface = outDummy.cValueSurface;
                    out.pValueSurface = outDummy.pValueSurface;
                    out.probMeshInt = outDummy.probMeshInt;
                    
                     %% at T-dT call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0.000001;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVolPrev = outDummy.impVolSurface;
                    out.cValueSurfacePrev = outDummy.cValueSurface;
                    out.pValueSurfacePrev = outDummy.pValueSurface;
                    out.probMeshIntPrev = outDummy.probMeshInt;
                    
                    aaa = 1.0;
                    
                case 'bootstrapForwardOnly'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    aaa = 1.0;
                    
                    
                      

                otherwise
                    disp('unImplemented')
                    
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGFFixedGrid < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        numOfFactors
        
        %% pricingVolGrid data
        pricingForwardGrid
        pricingReducedForwardGrid
        pricingVolGrid
        pricingVolGridSize
        volNodeFwdCurve
        modelStatesFixedGrid
        basePrice
        %% fixed Strike
        settleFutures
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGFFixedGrid(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
%                     eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')= 'matlabMonotonCubicSplineMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;
                
                eqCOMDupireSpotGF.pricingForwardGrid = [];
                eqCOMDupireSpotGF.pricingReducedForwardGrid = [];
                eqCOMDupireSpotGF.pricingVolGrid = [];
                eqCOMDupireSpotGF.volNodeFwdCurve = [];
                eqCOMDupireSpotGF.modelStatesFixedGrid = [];
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            try
                fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            catch ME
                aaa = 0;
            end
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    aaa =1.0;
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end   
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabMonotonCubicSplineMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                % monotonic cubic spline interpolation
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),3);
                end     
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
          
        function localVol = GetLocalVolFromProxyFixedGrid(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow,ratio)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            try
                fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            catch ME
                aaa = 0;
            end
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    aaa =1.0;
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(Ks)
%                     localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                    localVol(i) = H_interpolation(volProxyKs,volProxy,ratio*Ks(i),1);
                end   
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabMonotonCubicSplineMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                % monotonic cubic spline interpolation
                for i=1:length(Ks)
%                     localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),3);
                    localVol(i) = H_interpolation(volProxyKs,volProxy,ratio*Ks(i),3);
                end     
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function newP = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP, basePrice)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
%             ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            ipos = 0;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
%             proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            
            fwdNM = eqCOMDupireSpotGF.FwdNM(fromTime);
            ratio = basePrice/fwdNM;
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxyFixedGrid(volProxy,Ks,ipos,idxNow,ratio);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function newP = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = log(Ks(2)/Ks(1));
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
            for i=1:size
                temp = 0.5*dT*proxy(i)*proxy(i)/dK;
                a(i) = -temp*(1.0/dK + 0.5);
                b(i) = 1 + 2.0/dK*temp;
                b_rg(i) = b(i) - 1.0;
                c(i) = -temp * (1.0/dK - 0.5);
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function newP = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);
            
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
%             dK2 = dK*dK;
%             for i=1:size
%                 temp = 0.5*dT*proxy(i)*proxy(i)/dK;
%                 a(i) = -temp*(1.0/dK);
%                 b(i) = 1 + 2.0/dK*temp;
%                 b_rg(i) = b(i) - 1.0;
%                 c(i) = -temp*(1.0/dK);
%             end
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1));
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            % we use the same linear interpolation scheme as calibration
            useVolProxyInterpolationYN = 'YES';
            if strcmp(useVolProxyInterpolationYN,'YES')
                if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabMonotonCubicSplineMarketFwdMoneyness')
                    for ii =1:length(x)
                        localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),3);
                    end
                elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol'),'matlabLinearMarketFwdMoneyness')
                    for ii =1:length(x)
                        localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
                    end
                else
                    for ii =1:length(x)
                        localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
                    end
                end
            else
                volKnotPoints = zeros(length(ipos),1);
                for i=1: length(ipos)
                    volKnotPoints(i) = Ks(ipos(i));
                end


                for i=1:length(x)
                    xIdx = find(volKnotPoints <=x(i));
                    if isempty(xIdx)
                        localVol(i) = localVolLine(1);
                    elseif max(xIdx) == ipos(length(ipos))
                        localVol(i) = localVolLine(length(ipos));
                    else
                        localVolIdx = max(xIdx);
                        weight = (x(i)-Ks(ipos(localVolIdx)))/(Ks(ipos(localVolIdx)+1)-Ks(ipos(localVolIdx)));
                        localVol(i) = weight*localVolLine(ipos(localVolIdx)+1)+(1-weight)*localVolLine(ipos(localVolIdx));
                    end
                end
            end
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U,Ks)
            
            NMC = length(lastX);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U)
            
            NMC = length(lastX);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end

        function mcmcOut = inductMCForwardFineVolGrid(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime + 0.01);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
    
            Ks = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            proxy = eqCOMDupireSpotGF.pricingVolGrid(idxNow,:);

            localVol = zeros(length(predictor),1);

            for ii=1:length(predictor)
                localVol(ii) = H_interpolation(Ks,proxy,predictor(ii),1);
            end

%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, ~,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNMFixedGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             
             volNodeFwdCurve = eqCOMDupireSpotGF.volNodeFwdCurve;
             
             volNodeFwdSize = size(volNodeFwdCurve,1);
             volNodeFwdMaturity = volNodeFwdCurve(:,1); 
             idxVol = find(observeTime <= volNodeFwdMaturity);
             if isempty(idxVol)
                idxVolNM = volNodeFwdSize;
             else
                idxVolNM = min(idxVol);
             end
             
             fwd_VolNM = volNodeFwdCurve(idxVolNM,2);
             basePrice = eqCOMDupireSpotGF.basePrice;
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM/fwd_VolNM * basePrice * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMFinePDEGrid(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SMCFlat(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % flat vol 0.35
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            eqCOMDupireSpotGF.localVolSurface.volProxy = ones(size(fwdMoneyness))*0.35;
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end

        function out = computeStepdown1SMCFineVolGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;


            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    mcmcOut   = inductMCForwardFineVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 40000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*df_ep;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = meshC;
                
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    contiValueC = nMFuture.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = contiValueC;
                    
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*onePayoffD;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = unhitValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SGFFixedGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% fixedGrid generation start
            
            basePrice = stepdownParams.params('basePrice');
            
            %% PricingIdx & WeightNextPriceIndex update
           PricingIdx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           %nearest futures at evaluation
           fwdNM = eqCOMDupireSpotGF.FwdNM(0);
           spotLevel = fwdNM/basePrice;
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           %% fixedGrid fwd
           fwdNM = eqCOMDupireSpotGF.FwdNM(currentTime);
           comFwd = comFwd/fwdNM*basePrice;
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
                    meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                     %% fixedGrid fwd
                    fwdNM = eqCOMDupireSpotGF.FwdNM(currentTime);
                    comFwd = comFwd/fwdNM*basePrice;
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    %% fixedGrid fwd
                    fwdNM = eqCOMDupireSpotGF.FwdNM(currentTime);
                    comFwd = comFwd/fwdNM*basePrice;
                    
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SGFPricingVolGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            
            % grid size is log equi distant with 0.5% size
            dy = 0.005;
            volATM = impVolSurf(size(volProxy,1),round(size(volProxy,2)+1)/2);
            

%             X_max = max(1.3*fwdNM(size(volProxy,1)),basePrice*exp(5.0*volATM*sqrt(expiry(size(volProxy,1))/365.0)));
%             X_min = min(0.7*fwdNM(size(volProxy,1)),basePrice*exp(-5.0*volATM*sqrt(expiry(size(volProxy,1))/365.0)));
%             
            X_max = basePrice*exp(5.0*volATM*sqrt(expiry(size(volProxy,1))/365.0));
            X_min = basePrice*exp(-5.0*volATM*sqrt(expiry(size(volProxy,1))/365.0));
            
            K = round(log(X_max/X_min)/dy);
            temp_pricingForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingForwardGrid(i,j) = X_min*exp((j-1)*dy);
                      temp_pricingReducedForwardGrid(i,j) = temp_pricingForwardGrid(i,j)/fwdNM(i);
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid/basePrice;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
%            basePrice = stepdownParams.params('basePrice');
           
            %nearest futures at evaluation
           fwdNM  =  eqCOMDupireSpotGF.FwdNM(0);
           fwdVolNM = eqCOMDupireSpotGF.volNodeFwdCurve(1,2);
                   
           spotLevel = fwdVolNM/basePrice;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
                    mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SGFFinePDEGrid(eqCOMDupireSpotGF,valueDate,stepdownParams)
            %% generate local vol pricing grid start
            basePrice = stepdownParams.params('basePrice');
            eqCOMDupireSpotGF.basePrice = basePrice;
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy;
            fwdMoneyness = eqCOMDupireSpotGF.fwdMoneyness;
            impVolSurf = eqCOMDupireSpotGF.mktData('impliedVolSurface').volSurfaceR;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            fwdNM = zeros(size(expiry));
            for i=1:length(fwdNM)
                fwdNM(i) = eqCOMDupireSpotGF.FwdNM(expiry(i));
            end
            
            % grid size is log equi distant with 0.5% size
            dy = 0.0025;
              
            X_max = 2.5;
            X_min = 0.1;
            
            K = round((X_max-X_min)/dy);
            temp_pricingReducedForwardGrid = zeros(size(volProxy,1),K+1);
            temp_pricingVolGrid = zeros(size(volProxy,1),K+1);

            pricingVolGridSize = K+1;
            
            for i=1:size(volProxy,1)
                fwdMoneynessPerExpiry = fwdMoneyness(i,:);
                volProxyPerExpiry = volProxy(i,:);
                
                for j=1:K+1
                      temp_pricingReducedForwardGrid(i,j) = X_min + (j-1)*dy;
                      temp_pricingVolGrid(i,j) = H_interpolation(fwdMoneynessPerExpiry,volProxyPerExpiry,temp_pricingReducedForwardGrid(i,j),1);
                end
            end
            
            volNodeFwdCurve = zeros(length(expiry),2);
            
            for i=1:length(expiry)
                volNodeFwdCurve(i,1) = expiry(i);
                volNodeFwdCurve(i,2) = fwdNM(i);
            end
            
            pricingForwardGrid = temp_pricingReducedForwardGrid(end,:);
            pricingReducedForwardGrid = pricingForwardGrid;
            pricingVolGrid = temp_pricingVolGrid;
                
            eqCOMDupireSpotGF.pricingForwardGrid = pricingForwardGrid;
            eqCOMDupireSpotGF.pricingReducedForwardGrid = pricingReducedForwardGrid;
            eqCOMDupireSpotGF.pricingVolGrid = pricingVolGrid;
            eqCOMDupireSpotGF.volNodeFwdCurve = volNodeFwdCurve;
            
            %% pricing PDE Grid
            
            modelStatesFixedGrid = eqCOMDupireSpotGF.pricingReducedForwardGrid;
            modelStates = modelStatesFixedGrid;
            eqCOMDupireSpotGF.modelStatesFixedGrid = modelStatesFixedGrid;
            modelStatesSize = length(modelStatesFixedGrid);
          
            %% generate pricingVolGrid for localVol look-up & also for pricing fixed grid end
            
            
          %% PricingIdx & WeightNextPriceIndex update start
           
           spotLevel = 1.0;
           
           isFoundSpotLevel = 'false'; 
           for i=1:modelStatesSize-1
               
               if spotLevel >= modelStates(i) && spotLevel < modelStates(i+1)
                   PricingIdx = i;
                   WeightNextPriceIndex = (spotLevel - modelStates(i))/(modelStates(i+1)-modelStates(i));
                   isFoundSpotLevel = 'true';
                   break;
               end
           end
           
           if strcmp(isFoundSpotLevel,'false')
               error('spot price is out of grid range!');
           end
           
          %% PricingIdx & WeightNextPriceIndex update end
            
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.modelStatesFixedGrid;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
          
          %% fixedGrid fwd
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
           comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
           
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
%                     mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
%                     mesh  = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh,basePrice);
%                     meshB = inductGFBackwardFixedGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB,basePrice);
                    
%                     mesh  = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackwardPricingVolGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    
                    mesh  = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackwardFinePDEGrid(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                  %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                   
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                 %% fixedGrid fwd
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMFixedGrid(currentTime);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMFinePDEGrid(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           
            %% interpolate on the grid
            hitValue.npv = (1-WeightNextPriceIndex)*hitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*hitValue.payoff(PricingIdx+1);
                             
            unhitValue.npv = (1-WeightNextPriceIndex)*unhitValue.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*unhitValue.payoff(PricingIdx+1);
                             
            nMFuture.npv = (1-WeightNextPriceIndex)*nMFuture.payoff(PricingIdx) ...
                                 + WeightNextPriceIndex*nMFuture.payoff(PricingIdx+1);                 
            
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           dummyMeshB = zeros(length(timeStep),2);
           dummyIdx = 1;
           dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
           dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
           dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                    %apply american option
                    comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValueB  = meshB/onePayoffD;
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    if strcmp(vanillaParams.params('callPutFlag'),'C')
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
                            if payoffStateB.cashflow(j) > contiValueB(j)
                                ccc = 1.0;
                            end
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                        
                    else
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                    end
                    payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
                    meshB = payoffStateB.cashflow_npv;
                    dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
                    dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
                    dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = europeanValue.payoff(Pricingidx);
           americanValue.npv = americanValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            
            initX = ones(NMC,1);
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                nextX = eqCOMDupireSpotGF.inductMCForward(timeStep(i-1),timeStep(i),startIdx,endIdx,timeScheduleInfo,nextX,dZStep,params);
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            initX = ones(NMC,1);
            initXIdx = ones(NMC,1)*params.Pricingidx;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            nextXIdx = initXIdx;
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextX,nextXIdx,U(:,i-1),Ks);
                nextX = mcmcOut.nextX;
                nextXIdx = mcmcOut.nextXIdx;
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
            newTimeSchedule = sort(union(volExpiry,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
            MCTimeStep = length(expiry); % -1 because 0

            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            
            
          %% Solve  Forward PDE(GF) One time
            outGF = eqCOMDupireSpotGF.Solve1DGF(tvar,mkt_dT,optParams.dK,optParams.lastProb,optParams);
            
            newProb = outGF.newProb;
            optParams.meshProb = newProb;
           %% PDE(GF) Solve End
           % find the implied vol of dupire model
           if strcmp(eqCOMDupireSpotGF.modelParams('UseLetsBeRational'),'YES')
               target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           else
               target = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           end
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,dT,lastProb,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.fwdMoneyness(idxNow,i);
            end
                
%             if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
%                 % market strike points in fwd PDE grid
%                 fwdFactor = eqCOMDupireSpotGF.FwdFactor(params.expiry(idxNow));
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i)/fwdFactor;
%                 end
%             else
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i);
%                 end
%             end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastProb = lastProb;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;
            
            if idxNow <= numOfCutoffTenor
                lowerIdx = min(find(optParams.marketStrikes >= lowerCutoff));
                upperIdx = max(find(optParams.marketStrikes <= upperCutoff));
            end
            
            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
%             tol = 0.0001;
%             maxIter = 1000;
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
            out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            bootStrapOut.lastProb = out.newProb;
            bootStrapOut.condProb = out.condProb;
            
        end
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            if strcmp(volSurface.params('moneyNessType'),'fixedStrike')
                settleFutures = eqCOMDupireSpotGF.modelParams('settleFutures');
                eqCOMDupireSpotGF.settleFutures = settleFutures;
                for k=1:expirySize
                     fwd = settleFutures(k);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j)/fwd;
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
    
            elseif strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess')
                for k=1:expirySize
    %                 fwd = black.Fwd(spot,expiry(k));
    %                 df = black.zeroCurve.DF(expiry(k)/365.0);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize

                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        if strike(j) <= 0
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        else
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        end

                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'P');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'C');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        end
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                         
                    end
                    dfOut(k) = black.zeroCurve.DF(expiry(k)/365.0);
                end
                
            end
                
%             if strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         fwdStrike = strike(j)/fwdFactor;
%                         if fwdStrike <= 1.0
% %                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                         else
% %                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                             blackOTMPrices(k,j)  = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                             
%                         end
%                     end
%                 end
%             else
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         if strike(j) <= 1
%                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                         else
%                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                         end
%                     end
%                 end
%             end
%             
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
            params.fwdMoneyness = fwdMoneyness;
            
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            
            %initialze the intial probability distribution in the grid
            initProb = zeros(1,params.Ns);
            initProb(params.Pricingidx) = 1.0;
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;
            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
%                     toc
                    
%                     tic
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    params.marketStrikes = out.marketStrikes;
                    
%                     toc
                    
%                     calculate backward scheme for given target
%                     compareforwardMCFlag = 1 for one step euler scheme
%                     compareforwardMCFlag = 2 for daily euler scheme
%                     
%                     compareforwardMCFlag = 3 for markov chain monte carlo
                     
                    
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
  
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end

%                     toc
                case 'bootstrapForward'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    % compute implied surface for targetStrikes;
                    targetExpiry = params.expiry;
                    
                    %% at T call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVol = outDummy.impVolSurface;
                    out.cValueSurface = outDummy.cValueSurface;
                    out.pValueSurface = outDummy.pValueSurface;
                    out.probMeshInt = outDummy.probMeshInt;
                    
                     %% at T-dT call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0.000001;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVolPrev = outDummy.impVolSurface;
                    out.cValueSurfacePrev = outDummy.cValueSurface;
                    out.pValueSurfacePrev = outDummy.pValueSurface;
                    out.probMeshIntPrev = outDummy.probMeshInt;
                    
                    aaa = 1.0;
                    
                case 'bootstrapForwardOnly'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    aaa = 1.0;
                    
                    
                      

                otherwise
                    disp('unImplemented')
                    
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpotGF < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        localVolSurface
        modelSchedule
        fwdMoneyness
        numOfFactors
    end
    
    methods
        function eqCOMDupireSpotGF = EQCOMDupireSpotGF(EQModel)
            if nargin > 0
                eqCOMDupireSpotGF.zeroCurve = EQModel.zeroCurve;
                eqCOMDupireSpotGF.dividendCurve = EQModel.dividendCurve;
                eqCOMDupireSpotGF.repoRateCurve = EQModel.repoRateCurve;
                eqCOMDupireSpotGF.forwardCurve = EQModel.forwardCurve;
                
                eqCOMDupireSpotGF.spot = EQModel.spot;
                eqCOMDupireSpotGF.mktData =  EQModel.mktData;
                eqCOMDupireSpotGF.modelParams = EQModel.modelParams;
                
                if ~isKey(EQModel.modelParams,'LocalVolInterpol')
                    eqCOMDupireSpotGF.modelParams('LocalVolInterpol')='matlabLinearMarketFwdMoneyness';
                end
                
                if ~isKey(EQModel.modelParams,'VolProxyOnMarketStrikeYN')
                    eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN')='No';
                end
                
                if ~isKey(EQModel.modelParams,'UseLetsBeRational')
                   eqCOMDupireSpotGF.modelParams('UseLetsBeRational')='YES';
                end
                
                if ~isKey(EQModel.modelParams,'localVolFloor')
                   eqCOMDupireSpotGF.modelParams('localVolFloor')= 0.0001;
                end
                
                if ~isKey(EQModel.modelParams,'localVolCap')
                   eqCOMDupireSpotGF.modelParams('localVolCap')= 5.0;
                end
                
                eqCOMDupireSpotGF.modelSchedule = [];
                eqCOMDupireSpotGF.fwdMoneyness = [];
                
                % 1 factor local vol model
                eqCOMDupireSpotGF.numOfFactors = 1;
            end
        end
        
        function out= expmReghai(eqCOMDupireSpotGF,A,t)
            % Scale A by power of 2 so that its norm is < 1/2 .
            A = A*t;
            [f,e] = log2(norm(A,'inf'));
            s = max(0,e+1);
            A = A/2^s;
            Aexp = eye(size(A,1)) + A;
            testflag = 0;
%             tic
            if ~testflag
                for i=1:s
                    Aexp = Aexp*Aexp;
                end
            else
                D =Aexp;
                B= Aexp;
                E = zeros(size(A,1),size(A,1));
                for i=1:s
                    E = D*B;
                    D = E;
                    B = E;
                end
                Aexp = E;
            end
%             toc
            out = Aexp;
        end
        
        function path= bbgenerator(eqCOMDupireSpotGF,rn)
            %generate brownian bridge 
            
            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; 
            rightweight(1)=1; 
            j=1;
            for i=2:Nsteps    
                while map(j) 
                    j=j+1;
                end
                k=j;
                while ~map(k) 
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqCOMDupireSpotGF,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqCOMDupireSpotGF,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [ x,y,d] = HugeDecomp(eqCOMDupireSpotGF,n,a,b,c)
    
            x = zeros(n,1);
            y = zeros(n,1);
            d = zeros(n,1);
            %fwd

            x(1) = 1.0;
            x(2) = 1.0;

            for i=3:n
                x(i) = x(i-1) - (a(i-1)/b(i-1))*(c(i-2)/b(i-2))*x(i-2);
            end

            %bwd
            y(n) = 1.0/(x(n)-(a(n)/b(n))*(c(n-1)/b(n-1))*x(n-1));
            y(n-1) = y(n);

            for i=n-2:-1:1
                y(i) = y(i+1) - (a(i+2)/b(i+2))*(c(i+1)/b(i+1))*y(i+2);
            end

            %set d

            d(1) = x(1)*y(1)/b(1);
            for i=2:n
                d(i) = -(a(i)/b(i))*(y(i)/y(i-1))*d(i-1) + x(i)*y(i)/b(i);
            end


        end

        
        function localVol = GetLocalVolFromProxy(eqCOMDupireSpotGF,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            try
                fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            catch ME
                aaa = 0;
            end
            
            if strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqCOMDupireSpotGF.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    aaa =1.0;
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqCOMDupireSpotGF.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = fwdMoneynessPerExpiry(i);
                end
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end   
                
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
                        
        
        function [newC newP] = Solve1DPDE(eqCOMDupireSpotGF,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
            pmeshC = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = Solve1DGF(eqCOMDupireSpotGF,tvar,dT,dK,lastProb,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastProb),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

            %filling end
            
            meshProb = lastProb;
            
            size = length(meshProb);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            
            condProb = zeros(size,size);
            if optParams.params.GFType == -1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
%                 tic
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
%                 toc
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 0
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            
            elseif optParams.params.GFType == 1
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newProb = lastProb*A_exp1;
                condProb =A_exp1;
            elseif optParams.params.GFType == 2
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newProb = lastProb;
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*A_exp1;
                    condProb = A_exp1*A_exp1;
                end
                
            elseif optParams.params.GFType == 3
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                newProb = newProb*oneStep;
                
                condProb = oneStep;
                
            else
                oneStepDt = optParams.params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
            
                % Test for HugeDecomposition for inverse matrix
                [ x,y,d] = eqCOMDupireSpotGF.HugeDecomp(size,a,b,c);
                A = gallery('tridiag',a1,b,c1);
                oneStep = OneStepGF(size,x,y,d,A);
                newProb = lastProb;
                %numberOfTimeStep;
                %oneStepDt = 1.0/365;
                
                condProb = eye(size,size);
                for t=1:NT
                    newProb = newProb*oneStep;
                    condProb = oneStep*oneStep;
                end 
                
            end
            
            out.newProb = newProb;
            out.condProb = condProb;
        end
        
        function newP = inductPDEBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP,params)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = params.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = params.Ks(2) - params.Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            if params.backGFType == -1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
                newP = A_exp1*lastP;
                
            elseif params.backGFType == 0
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expmdemo1(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 1
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg*NT);
                newP = A_exp1*lastP;
            elseif params.backGFType == 2
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == -21
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                A_rg = full(gallery('tridiag',-a1*oneStepDt/dT,-b_rg*oneStepDt/dT,-c1*oneStepDt/dT));
                A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,1.0);
%                 A_exp1 = expm(A_rg);
                
                newP = lastP;
                
                for t=1:NT
                    newP = A_exp1*newP;
                end
                
            elseif params.backGFType == 3

                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,lastP);

                
            elseif (params.backGFType == 4) || (params.backGFType == 14) || (params.backGFType == 24)
                oneStepDt = params.oneStepDt;
                NT = round(dT/oneStepDt);
                
                % rescale matrix element to smaller time step
                a= a*oneStepDt/dT;
                b = (b-1)*oneStepDt/dT + 1.0;
                c = c*oneStepDt/dT;
                
                a1 = a(2:size);
                c1 = c(1:size-1);
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqCOMDupireSpotGF.LUDecompose(tdma);
                
                newP = lastP;
                for t=1:NT
                    newP = eqCOMDupireSpotGF.TDMASolve(tdmaLU,newP);
                end

            else 
                disp('unImplemented')
            end
        end
        
        function newP = inductGFBackward(eqCOMDupireSpotGF,fromTime,toTime,lastP)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (fromTime - toTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = A_exp1*lastP;
            
        end
        
        function out = generateCondProb(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            idx = find(expiry > fromTime & expiry < toTime);
            if isempty(idx)
                out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime);
            else
                
                timeStep = expiry(idx);
                defaultTimeStep = [fromTime;toTime];
                timeStep = sort(union(timeStep,defaultTimeStep),'ascend');
                condProbOneStep = zeros(length(Ks),length(Ks));
                condProb = eye(length(Ks),length(Ks));
                
                for i=1:length(timeStep)-1
                    condProbOneStep = generateCondProbOneStep(eqCOMDupireSpotGF,timeStep(i),timeStep(i+1));
                    condProb = condProb*condProbOneStep;
                end
                
                out =  condProb;
            end
            
            
        end
        
        function out = generateCondProbOneStep(eqCOMDupireSpotGF,fromTime,toTime)
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(Ks),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);
            %filling end
            
            size = length(proxy);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = (toTime - fromTime)/365.0;
            
            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end
            
            a(1) = 0;
            c(size) = 0;
            
            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;
            
            b(1) = 1;
            b(size) = 1;
            
            % to create tridiagonal matrix
            
            a1 = a(2:size);
            c1 = c(1:size-1);
            
            b_rg(1) = 0;
            b_rg(size) = 0;
            
            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            out = A_exp1;
            
        end
        
        function marginal = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry >= toTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            marginal(:,:) = eqCOMDupireSpotGF.localVolSurface.marginal(idxNow,:,:);
        end
        
        function localVol = InterpolateLocalVol(eqCOMDupireSpotGF,x,fromTime)

            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            idx = find(eqCOMDupireSpotGF.localVolSurface.expiry > fromTime);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            localVolLine = eqCOMDupireSpotGF.localVolSurface.localVol(idxNow,:);
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %             Ks = params.Ks;
            localVol =  zeros(length(x),1);
            fwdMoneynessPerExpiry = eqCOMDupireSpotGF.fwdMoneyness(idxNow,:);
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            % we use the same linear interpolation scheme as calibration
            useVolProxyInterpolationYN = 'YES';
            if strcmp(useVolProxyInterpolationYN,'YES')
                
                for ii =1:length(x)
                    localVol(ii) = H_interpolation(fwdMoneynessPerExpiry,volProxy,x(ii),1);
                end
            else
                volKnotPoints = zeros(length(ipos),1);
                for i=1: length(ipos)
                    volKnotPoints(i) = Ks(ipos(i));
                end


                for i=1:length(x)
                    xIdx = find(volKnotPoints <=x(i));
                    if isempty(xIdx)
                        localVol(i) = localVolLine(1);
                    elseif max(xIdx) == ipos(length(ipos))
                        localVol(i) = localVolLine(length(ipos));
                    else
                        localVolIdx = max(xIdx);
                        weight = (x(i)-Ks(ipos(localVolIdx)))/(Ks(ipos(localVolIdx)+1)-Ks(ipos(localVolIdx)));
                        localVol(i) = weight*localVolLine(ipos(localVolIdx)+1)+(1-weight)*localVolLine(ipos(localVolIdx));
                    end
                end
            end
            
        end
        
        function out = inductMCMCForward(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U,Ks)
            
            NMC = length(lastX);
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function out = inductMCMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,lastXIdx,U)
            
            NMC = length(lastX);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            % we generate conditional probability matrix first
            condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            Qa = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProb,Ks);
            
%             Qa = InterpolateMarginal(eqCOMDupireSpotGF,fromTime,toTime);
            uSample = U;
            
            nextX = zeros(NMC,1);
            nextXIdx = zeros(NMC,1);
%             Ks = params.Ks;
            nPoints = length(Ks);
            
            for i=1:NMC
                IndexMc = lastXIdx(i);
                j= IndexMc;
                cumProb = Qa(IndexMc,:);
                idxH = min(find(uSample(i)*Qa(IndexMc,end) < cumProb));
                nextX(i) = Ks(idxH);
                nextXIdx(i) = idxH;

            end
            
            out.nextX = nextX;
            out.nextXIdx = nextXIdx;

            
        end
        
        function newX = inductMCForward(eqCOMDupireSpotGF,fromTime,toTime,startIdx,endIdx,timeScheduleInfo,lastX,dZ,params)
            
            timeSchedule = timeScheduleInfo.timeSchedule;
            dTSchedule365 = timeScheduleInfo.dTSchedule365;
            volKnotIdx = timeScheduleInfo.volKnowIdx;
            
            predictor = lastX;
            for j=startIdx:endIdx-1
                
                localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,timeSchedule(j));
                Dt = dTSchedule365(j);
                sqrtDt = sqrt(dTSchedule365(j));
                for i=1:length(lastX)
                    predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
%                     predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i,j-startIdx+1)); 
                end
            end
            newX = predictor;
            
        end
        
        function mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
            localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function out = ComputePutOTMPricesMCMC(eqCOMDupireSpotGF,StrikeSim,nextXIdx,fromTime,toTime)
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            if fromTime == toTime-1
                bbb = 1.0;
            end
            
            if fromTime == toTime
                condProb = eye(length(Ks));
            else
                condProb = eqCOMDupireSpotGF.generateCondProb(fromTime,toTime);
            end
            
            SpotMCMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,Ks);
            putOTM = zeros(length(nextXIdx),1);
            
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);
            
            df_ft = df_t/df_f;
            putOTMPrices = zeros(length(Ks),1);
            
            for i=1:length(nextXIdx)
                transProb = condProb(nextXIdx(i),:);
                % vectorization
                putOTMPrices = max(StrikeSim(i)*ones(length(transProb),1) - SpotMCMC,0);
                putOTM(i) = transProb*putOTMPrices;
                
            end
            
            putOTM = putOTM*df_ft;
            out = putOTM;
            
        end
        
        function out = ComputePutOTMPricesMC(eqCOMDupireSpotGF,StrikeSim,nextX,fromTime,toTime,nestedU,nestedNMC,nestedMCOneTimeStep)

            putOTM = zeros(length(nextX),1);
            putOTMPrices = zeros(nestedNMC,1);
            
            if fromTime == toTime
                for i=1:length(nextX)
                    SpotMC = eqCOMDupireSpotGF.EQSpotMC(toTime,nextX(i));
                    % vectorization
                    putOTM(i) = max(StrikeSim(i) - SpotMC,0);
                   
                end
            
            else

                df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
                df_t = eqCOMDupireSpotGF.zeroCurve.DF(toTime/365.0);

                df_ft = df_t/df_f;
                

                %daily timeSteps
                nestedMCTimeStepsSize = toTime - fromTime;
                nestedTimeStep = [toTime:-1*nestedMCOneTimeStep:fromTime]';
                defaultTimeStep = [fromTime; toTime];
                
                nestedTimeStep = sort(union(defaultTimeStep,nestedTimeStep),'ascend');
                
                expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
                idx = find(expiry > fromTime & expiry < toTime);
                if ~isempty(idx)
                    volTimeStep = expiry(idx);
                    nestedTimeStep = sort(union(volTimeStep,nestedTimeStep),'ascend');
                end
                
                nestedMCTimeStepsSize = length(nestedTimeStep);
                
                for i=1:length(nextX)
                    nestedNextX = nextX(i)*ones(nestedNMC,1);
                    for j=1:nestedMCTimeStepsSize-1
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,nestedTimeStep(j),nestedTimeStep(j+1),nestedNextX,nestedU(:,j));
                        nestedNextX = mcmcOut.nextX;
                    end

                    SpotMC = eqCOMDupireSpotGF.EQSpotMCMC(toTime,nestedNextX);
                    % vectorization
                    putOTMPrices = max(StrikeSim(i)*ones(length(nestedNMC),1) - SpotMC,0);
                    putOTM(i) = mean(putOTMPrices);

                end
                
                putOTM = putOTM*df_ft;
            end
            
            
            out = putOTM;
            
        end
        
        function out = UpdatePutShortIndex(eqCOMDupireSpotGF,indexSim,fixingS,prevOTM,currOTM,fromTime,toTime)
%             cd = 
            df_f = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0);
            df_fterm = eqCOMDupireSpotGF.zeroCurve.DF(fromTime/365.0 + 0.25);
            fwdCD = (df_f/df_fterm -1.0)/0.25; 
            dt = (toTime-fromTime)/365.0;
            
            indexUpDate = zeros(length(indexSim),1);
            for i=1:length(indexSim)
                indexUpDate(i) = indexSim(i)*(1+ (-currOTM(i)+prevOTM(i))/fixingS(i) + (1-0.075)*fwdCD*dt);
            end
            
            out = indexUpDate;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
                    out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,meshProb,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            cValue = meshProb*meshC;
            pValue = meshProb*meshP;
            
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                if K <= 1.0
%                      out.vols(i) = blackVolLBR(pValue(i),1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,pValue(i),Tol,MaxIter); 
                     out.interpOTMPrices(i) = pValue(i);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                     
                else
%                     out.vols(i) = blackVolLBR(cValue(i),1.0,K,params.params.expiry(idxNow)/365.0,1);
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K,0.0,params.params.expiry(idxNow)/365.0,a,b,cValue(i),Tol,MaxIter); 
                    out.interpOTMPrices(i) = cValue(i);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = computeBackwardPDEOne(eqCOMDupireSpotGF,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- modelX(i),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            else
                for i=1:modelXSize
                    mesh(i,1) = max(modelX(i)-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqCOMDupireSpotGF.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,params);
                end
                
                out = mesh(params.Pricingidx);
                
            end
            
        end
        
        function columnOut = MCPayoff(eqCOMDupireSpotGF,idx,comFwd,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwd);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwd(idx11) >= basePrice*strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwd(idx11)/basePrice;
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwd(idx11) < basePrice*callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwd(idx11)/basePrice;
                            elseif comFwd(idx11) < basePrice*strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwd(idx11)/basePrice - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwd(idx11) > basePrice*lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function columnOut = MCPayoffWorst(eqCOMDupireSpotGF,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
%             
%             columnOut.isStop = zeros(scheduleSize,modelStatesSize);
%             columnOut.worstP = zeros(scheduleSize,modelStatesSize);
%             
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
%             columnOut.payoffColumn = PricerInfo(1, modelStatesSize);
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = EQSpotMCMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotMCGeneric(eqCOMDupireSpotGF,valueDate,observeTime,modelStates)
            
            if observeTime <0
                allFixings = eqCOMDupireSpotGF.modelParams('allFixings');
                fixingDate = AddDate(valueDate,observeTime,'day');
                
                fixingTicker = 'equityIndex';
                
                eqIndexFixings = allFixings(fixingTicker);
                
                try
                    fixing = eqIndexFixings(StrDate(fixingDate,'str'));
                    stateSize = size(modelStates,2);
                    out = ones(1,stateSize)*fixing;
                    
                catch exception
                    throw(exception)
                end
                
            else
                out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates);
                
                % transpose for genericPricing
                out = out';
                
            end
        end
        
        function out = EQSpotMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
            detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 
             
             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = EQSpotGenericMC(eqCOMDupireSpotGF,valueDate,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
            if observeTime < 0
                allFixings = eqCOMDupireSpotGF.modelParams('allFixings');
                fixingDate = AddDate(valueDate,observeTime,'day');
                equity1Fixings = allFixings('Equity1Index');
                try
                    fixing = equity1Fixings(StrDate(fixingDate,'str'));
                    stateSize = length(modelStates);
                    out = ones(stateSize,1)*fixing;
                    
                catch exception
                    throw(exception)
                end
            else
                spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
                detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

                 %stochasticFwd(0,T)
                 stateSize = length(modelStates);
                 stochasticFwd = zeros(stateSize,1);

                 for i=1:stateSize
                    stochasticFwd(i) = detFwd * modelStates(i); 
                 end

                 out = stochasticFwd;
            end
        end
        
        function out = EQFwdMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = fxDupireSpotGF.localVolSurface.Ks;
        spotPrice = eqCOMDupireSpotGF.spot.params('rawData');
        detFwd = eqCOMDupireSpotGF.Fwd(spotPrice,observeTime); 

         %stochasticFwd(0,T)
         stateSize = length(modelStates);
         stochasticFwd = zeros(stateSize,1);

         for i=1:stateSize
            stochasticFwd(i) = detFwd * modelStates(i); 
         end

         out = stochasticFwd;
        end
        
        % NM : nearest month forward
        function out = CommoFwdNM(eqCOMDupireSpotGF,observeTime)
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
           % NM : nearest month forward
        function out = CommoFwdContractM(eqCOMDupireSpotGF,observeTime,maturityTime)
            if observeTime > maturityTime
                disp('observeTime is passed maturityTime!')
                out = 0;
                return;
            end
            
            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(maturityTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = CommoFwdNMMC(eqCOMDupireSpotGF,observeTime,modelStates)
%             modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
            forwardCurve = eqCOMDupireSpotGF.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeConvertibleBond1SMCEQ(eqCOMDupireSpotGF,valueDate,convertibleBondParams)
%           
            % model schedule generation
            
            %% couponSchedule start
            
            couponScheduleInt = convertibleBondParams.params.couponInfo.couponScheduleInt;
            
            % schedule is couponSchedule
            % main backbone schedule
            scheduleSize = size(couponScheduleInt,1);
            couponSchedule= struct;
            % coupon payment event happens at endDate
            %eventTime is endDate
            % payment date can be different from endDate
            for i=1:scheduleSize
%                 couponSchedule.payDate(i) = H_Date(couponScheduleInt(i,4));
                couponStartDate = H_Date(couponScheduleInt(i,2));
                couponEndDate = H_Date(couponScheduleInt(i,3));
                couponPayDate = H_Date(couponScheduleInt(i,4));
                
                couponSchedule.dayCount(i) = couponEndDate.DateDiff(couponStartDate);
                couponSchedule.dayCountFraction(i) = couponSchedule.dayCount(i)/365.0; 
                
                couponSchedule.eventTime(i) = DateDiff(couponEndDate,valueDate);
                couponSchedule.payTime(i) = DateDiff(couponPayDate,valueDate);
                
%                 couponSchedule.strike(i) = scheduleInt(i,2);
%                 couponSchedule.coupon(i) = scheduleInt(i,3);
            end
            couponSchedule.scheduleSize = scheduleSize;
            
%             expiryDate = couponSchedule.payDate(scheduleSize);
            expiryDate = convertibleBondParams.endDate;
            
            %% coupon schedule end
            
            %% puttable schedule start
            %% put exercise event happens the same date of payment
            puttableScheduleInt = convertibleBondParams.params.puttableInfo.puttableScheduleInt;
            puttableScheduleSize = size(puttableScheduleInt,1);
            puttableSchedule= struct;
            for i=1:puttableScheduleSize
                putExerciseDate = H_Date(puttableScheduleInt(i,1));
                
                puttableSchedule.eventTime(i) = DateDiff(putExerciseDate,valueDate);
                puttableSchedule.payTime(i) = DateDiff(putExerciseDate,valueDate);
                puttableSchedule.putPayment(i) = puttableScheduleInt(i,2);
            end
            puttableSchedule.scheduleSize = puttableScheduleSize;
            
           %% puttable schedule end
           
            %% call exercise event happens the same date of payment
            %% callable schedule start
            callableScheduleInt = convertibleBondParams.params.callableInfo.callableScheduleInt;
            callableScheduleSize = size(callableScheduleInt,1);
            callableSchedule= struct;
            for i=1:callableScheduleSize
                callExerciseDate = H_Date(callableScheduleInt(i,1));
                callableSchedule.eventTime(i) = DateDiff(callExerciseDate,valueDate);
                callableSchedule.payTime(i) = DateDiff(callExerciseDate,valueDate);
                
                 callableSchedule.callPayment(i) = callableScheduleInt(i,2);
            end
            callableSchedule.scheduleSize = callableScheduleSize;
            % condition on stockprice such that callable condition is
            % triggered
            callableConditionalStrike = convertibleBondParams.params.callableInfo.callableConditionalStrike;
            
           %% callable schedule end
           
           %% convertible info start
            
           %% refixing schedule start
            refixingScheduleInt = convertibleBondParams.params.convertibleInfo.refixingScheduleInt;
            refixingScheduleSize = size(refixingScheduleInt,1);
            refixingSchedule= struct;
            for i=1:refixingScheduleSize
                fixing1MStartDate = H_Date(refixingScheduleInt(i,1));
                fixing1WStartDate = H_Date(refixingScheduleInt(i,2));
                fixing1DStartDate = H_Date(refixingScheduleInt(i,3));
                refixingDate = H_Date(refixingScheduleInt(i,4));
                
                refixingSchedule.fixing1MStartEventTime(i) = DateDiff(fixing1MStartDate,valueDate);
                refixingSchedule.fixing1WStartEventTime(i) = DateDiff(fixing1WStartDate,valueDate);
                refixingSchedule.fixing1DStartEventTime(i) = DateDiff(fixing1DStartDate,valueDate);
                
                refixingSchedule.eventTime(i) = DateDiff(refixingDate,valueDate);
                refixingSchedule.payTime(i) = DateDiff(refixingDate,valueDate);
%                 refixingSchedule.payTime(i) = DateDiff(refixingDate,valueDate); 
            end
            refixingSchedule.scheduleSize = refixingScheduleSize;
            
            
          %% refixing schedule end
                %% convertible info
            initialConversionStrike = convertibleBondParams.params.convertibleInfo.conversionStrike;
            refixingStrikeGlobalFloor = convertibleBondParams.params.convertibleInfo.refixingStrikeGlobalFloor;
          %% convertible info end
            
            
          %% pricing time Step Generation start
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            
            aliveCoupon = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            eventTimeStep = volExpiry;
            if strcmp(eqCOMDupireSpotGF.modelParams('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                eventTimeStep = sort(union(eventTimeStep,dailyTimeSteps),'ascend');
            else
                error('for convertible bond we only use daily time steps!')
%                 timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
%                 dailyTimeSteps = [maturity:-timeStepP:0]';
%                 dailyTimeSteps = [dailyTimeSteps;0];
%                 timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
%             % we include couponPayDatees
%             expiredCoupon = 0;
%             aliveCoupon = 0;
%             for i= 1:scheduleSize
%                 daysToCoupon = couponSchedule.days(i);
%                 if daysToCoupon <= 0
%                     expiredCoupon = expiredCoupon +1;
%                     continue;
%                 else
%                     aliveCoupon = aliveCoupon + 1;
% %                     timeStep = [timeStep; daysToCoupon];
%                 end 
%             end
%             
%             lastAliveCouponIdx = 1 + expiredCoupon;
%             
%             % we include puttable schedule
%             expiredPut = 0;
%             alivePut = 0;
%             for i= 1:puttableScheduleSize
%                 daysToPut = puttableSchedule.days(i);
%                 if daysToPut <= 0
%                     expiredPut = expiredPut +1;
%                     continue;
%                 else
%                     alivePut = alivePut + 1;
% %                     timeStep = [timeStep; daysToPut];
%                 end 
%             end
%             
%             lastAlivePutIdx = 1 + expiredPut;
%             
%             % we include callable schedule
%             expiredCall = 0;
%             aliveCall = 0;
%             for i= 1:callableScheduleSize
%                 daysToCall = callableSchedule.days(i);
%                 if daysToCall <= 0
%                     expiredCall = expiredCall +1;
%                     continue;
%                 else
%                     aliveCall = aliveCall + 1;
% %                     timeStep = [timeStep; daysToCall];
%                 end 
%             end
%             lastAliveCallIdx = 1 + expiredCall;
%             % we include convertible schedule? no
%             % we just check whether we are in ther convertible possible period
%             
%             % we include refixing date
            
            
            eventTimeStep = sort(union(eventTimeStep,maturity),'ascend');
            
            aliveTimeStep = eventTimeStep(eventTimeStep>=0);
            aliveTimeStep = sort(aliveTimeStep,'ascend');
            
            totalAliveTimeStepSize = length(aliveTimeStep);
            
            % should we use eventTimeIdx as future only time stes?
            % In this case we better use more generic approach
            % such time all times steps are included 
            % and when payoff description is decoded, time should be
            % checked later
            
            
%             eventTimeIdx = zeros(couponSchedule.scheduleSize,1);
%             
%             for i= couponSchedule.scheduleSize:-1:lastAliveCouponIdx
%                 idx = find(timeStep == couponSchedule.days(i));
%                 eventTimeIdx(i) = min(idx);
%             end
           
          %% pricing time Step Generation end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalAliveTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalAliveTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
            
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = convertibleBondParams.params.nominal;
           basePrice = convertibleBondParams.params.basePrice;
           coupon = convertibleBondParams.params.couponInfo.coupon;
%            lowerBarrier = convertibleBondParams.params('lowerBarrier');
%            overHedgeShift = convertibleBondParams.params('overHedgeShift');
%            overHedgeSpread = convertibleBondParams.params('overHedgeSpread');
%            
%            callStrike1 = convertibleBondParams.params('callStrike1');
%            callValue1 = convertibleBondParams.params('callValue1');
%            SSpayoffYN = convertibleBondParams.params('SSpayoffYN');
%            KIYN = convertibleBondParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.initialConversionStrike = initialConversionStrike;
           payoffInfo.refixingStrikeGlobalFloor = refixingStrikeGlobalFloor;
%            payoffInfo.overHedgeSpread = overHedgeSpread;
%            
%            payoffInfo.callStrike1 = callStrike1;
%            payoffInfo.callValue1 = callValue1;
%            payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.couponSchedule = couponSchedule;
           payoffInfo.puttableSchedule = puttableSchedule;
           payoffInfo.callableSchedule = callableSchedule;
           payoffInfo.refixingSchedule = refixingSchedule;
           
           
           modelStatesSize = NMC;
           
          %% Define Pricing Columns
           % we need avg1MStockPrice, avg1WStockPrice,avg1DStockPrice,
           % floatingConversionStrike  <- all can be treated as
           % stateVariable
           
           % for the cashflow generated pricing columns as pricerInfo
           % we do not use pricerInfo Structure but simplified ones
           
          %% state variable initialize
%            worstP          = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           avg1MStockPrice = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           avg1WStockPrice = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           avg1DStockPrice = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           floatingConversionStrike = zeros(modelStatesSize,refixingSchedule.scheduleSize);
           
           stateVariables = containers.Map({'avg1MStockPrice','avg1WStockPrice'}, ...
                        {avg1MStockPrice,avg1WStockPrice});
                    
           stateVariables('avg1DStockPrice') = avg1DStockPrice;
           stateVariables('floatingConversionStrike') = floatingConversionStrike;
           
          %% PricingColumns that has cashflows
           % we have fixedCouponBond, convertibleOnlyBond,
           % puttableOnlyBond, convertibleAndPuttableBond,
           % convertiblePuttableCallableBond
                      
           %fixedCouponBond 
           fixedCouponBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %convertibleOnlyBond
           convertibleOnlyBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %puttableOnlyBond
           puttableOnlyBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %convertibleAndPuttableBond
           convertibleAndPuttableBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %convertiblePuttableCallableBond
           convertiblePuttableCallableBond = PricerInfoSimple(modelStatesSize,scheduleSize);
           %convertiblePuttableCallableBond
           convertibleOnlyBond = PricerInfoSimple(modelStatesSize,scheduleSize);
            %dummy floatingStrikeC
           floatingStrikeC= PricerInfoSimple(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use accruedSumOfStockPrice for moving average calculation 
           accruedSum1M = zeros(modelStatesSize,1);
           accruedSum1W = zeros(modelStatesSize,1);
           accruedSum1D = zeros(modelStatesSize,1);
           
           accruedDays1M = 0;
           accruedDays1W = 0;
           accruedDays1D = 0;
           
           previousConversionStrike = initialConversionStrike*ones(modelStatesSize,1);
           
            % we use all path for regression
            % conversion ITM , puttable ITM ,  callable ITM
            % what's the use of Alive Path only Regression Sampling ?
            
%            isStop = zeros(modelStatesSize,scheduleSize);
%            worstP = zeros(modelStatesSize,scheduleSize);
           
           
           % check whether current future price breach the barrier
%            comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
           comFwd = eqCOMDupireSpotGF.EQSpotGenericMC(valueDate,currentTime,nextX);
           
%           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
          %% Path Generation Forward
          %% Store (state) variables to be used for AMC Regression
           currentCouponPeriod = 1;
           %payoff descrption update index
           currentTimeIdx = 1;
           %MC numMethodState update index
           aliveTimeIdx = 1;
           % currentTimeStep is update in for statement
%            for currentTimeStep = eventTimeStep(1):1:eventTimeStep(end)
           for idxT = 1:1:length(eventTimeStep)
                currentTimeStep = eventTimeStep(idxT);
                % evaluate scripts 
                % evaluate stateVariables(stores)
                % evaluate expression per each pricing columns
                % at the end of the loop we induct forward
                % from left to right
                % fictional payoff script columns are
                % avg1MStockPrice,avg1WStockPrice,
                % avg1DStockPrice,floatingConversionStrke
                % worstP,fixedCouponBond,....
                
                % just evaluate spotPrice for the use in;
                comFwd = eqCOMDupireSpotGF.EQSpotGenericMC(valueDate,currentTimeStep,nextX);
                        
                % find the current
                % if find return errors then?
                try
                    % find the corresponding nearest future refixing event
                    idx = min(find(currentTimeStep <= refixingSchedule.eventTime));
                    
                  %% stateVariable avg1MStockPrice,avg1WStockPrice,avg1DStockPrice
                  %% floatingConversionStrike
                  
                    % if avg1MStockPrice evaluate condition is met
                    if currentTimeStep >= refixingSchedule.fixing1MStartEventTime(idx) ...
                       && currentTimeStep < refixingSchedule.eventTime(idx)
                   
                        accruedSum1M  = accruedSum1M + comFwd;
                        accruedDays1M = accruedDays1M +1;
                    end
                    
                    % if avg1WStockPrice evaluate condition is met
                    if currentTimeStep >= refixingSchedule.fixing1WStartEventTime(idx) ...
                       && currentTimeStep < refixingSchedule.eventTime(idx)
                   
                        accruedSum1W  = accruedSum1W + comFwd;
                        accruedDays1W = accruedDays1W +1;
                    end
                    
                    % if avg1DStockPrice evaluate condition is met
                    
                    if currentTimeStep >= refixingSchedule.fixing1DStartEventTime(idx) ...
                       && currentTimeStep < refixingSchedule.eventTime(idx)
                   
                        accruedSum1D  = accruedSum1D + comFwd;
                        accruedDays1D = accruedDays1D +1;
                    end
                    
                    % now if we are at refixingSchedule eventTime
                    % (refixingDate)
                    % fixingEventTime(idx)
                    % update floatingConversionStrike
                    if currentTimeStep == refixingSchedule.eventTime(idx)
                        
                        avg1MStockPrice(:,idx) =  accruedSum1M(:)/accruedDays1M;
                        avg1WStockPrice(:,idx) =  accruedSum1W(:)/accruedDays1W;
                        avg1DStockPrice(:,idx) =  accruedSum1D(:)/accruedDays1D;
                        
                        % save floatingConversionStrike per path, and
                        % update previousConversionStrike for the future
                        % use
                        for idx2=1:modelStatesSize
                            
                            floatingConversionStrike(idx2,idx) = min(previousConversionStrike(idx2,1),...
                                max(avg1MStockPrice(idx2,idx),avg1WStockPrice(idx2,idx),avg1DStockPrice(idx2,idx)));
                            
                            previousConversionStrike(idx2,1) = floatingConversionStrike(idx2,idx);
                        end
                        
                    end
                    
                 %% PricingColumns1: fixedCouponBond
                   idxCoupon = min(find(currentTimeStep <= couponSchedule.eventTime));
                   % if currentTime  is couponSchedule.eventTime
                  
                   if currentTimeStep == couponSchedule.eventTime(idxCoupon)
                        %fixedCouponCashflow
                         dcf = couponSchedule.dayCountFraction(idxCoupon);
                         payoffStateA.cashflow = nominal*coupon*dcf*ones(modelStatesSize,1);
                         df_e = 1.0;
                   end
                   
                    % if currentTimeSteps is today or future then inductMCForward
                    if currentTimeStep >= 0 && currentTimeStep < eventTimeStep(end)
                        nextTimeStep = eventTimeStep(currentTimeIdx +1);
                        mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,currentTimeStep,nextTimeStep,nextX,U(:,aliveTimeIdx));
                        nextX = mcmcOut.nextX;
                        %MC numMethodState update
                        aliveTimeIdx = aliveTimeIdx + 1;
                    end
                    
                    currentTimeIdx = currentTimeIdx +1;
                catch exception
                    throw(exception)
                end
                
                
           end
           
           bbb = 1.0;
           
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMCEQ(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
%                 NMC = 50000;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
%            comFwd = multiAsset.EQSpotMC(multiAsset.eqModelName,valueDate,currentTime, numMatTime, nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
%                 Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
%                     mcmcOut   = multiAsset.inductMCForwardNew(timeStep(idx),timeStep(idx+1),numMatTime,nextX,U(numOfFactors*(idx-1)+1:numOfFactors*(idx-1)+numOfFactors,:));
                    
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
%                     comFwd = multiAsset.EQSpotMC(multiAsset.eqModelName,valueDate,currentTime, numMatTime, nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqCOMDupireSpotGF.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        
        
        function out = computeStepdown1SMCMC(eqCOMDupireSpotGF,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 40000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqCOMDupireSpotGF.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
                columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
             
        function out = computeStepdown1SGF(eqCOMDupireSpotGF,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqCOMDupireSpotGF.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = unhitValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaGF(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
           modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = length(modelStates);
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           dummyMeshB = zeros(length(timeStep),2);
           dummyIdx = 1;
           dummyMeshB(dummyIdx,1) = eventTimeIdx(scheduleSize);
           dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
           dummyIdx = dummyIdx + 1;
           for i=scheduleSize:-1:lastAliveExerciseIdx
                % past schedule neglect
                startTimeIdx = eventTimeIdx(i);
                endTimeIdx = 1;  % valueDate
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = europeanValue.payoff;
                meshB = americanValue.payoff;
                meshC = nMFuture.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    if idx== 292
                        bbb =1.0;
                    end
                    mesh  = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),mesh);
                    meshB = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshB);
                    meshC = inductGFBackward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx-1),meshC);
                    % one step backward induction end
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    
                    %apply american option
                    comFwd = eqCOMDupireSpotGF.CommoFwdContractM(currentTime,maturity);
                    onePayoffD = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
                    contiValueB  = meshB/onePayoffD;
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    if strcmp(vanillaParams.params('callPutFlag'),'C')
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( comFwd(j) - strike,0);
                            if payoffStateB.cashflow(j) > contiValueB(j)
                                ccc = 1.0;
                            end
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                        
                    else
                        for j=1:modelStatesSize
                            payoffStateB.cashflow(j) = max( -comFwd(j) + strike,0);
                            payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                        end
                    end
                    payoffStateB.cashflow_npv = payoffStateB.cashflow*onePayoffD;
                    meshB = payoffStateB.cashflow_npv;
                    dummyMeshB(dummyIdx,1) = timeStep(lastTimeIdx);
                    dummyMeshB(dummyIdx,2) = payoffStateB.cashflow_npv(Pricingidx);
                    dummyIdx = dummyIdx + 1;
                end
                
                europeanValue.payoff = mesh;
                americanValue.payoff = meshB;
                nMFuture.payoff = meshC;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
           end
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = europeanValue.payoff(Pricingidx);
           americanValue.npv = americanValue.payoff(Pricingidx);
           nMFuture.npv = nMFuture.payoff(Pricingidx);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardStartingVanillaMC(eqCOMDupireSpotGF,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            startDate  = H_Date(vanillaParams.params('startDate'));
            
            scheduleSize = 2;
            % resetDate
            % expiryDate
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            daysToReset = DateDiff(startDate,valueDate);
            
            if maturity <=0
                out = 0;
                return;
            end
            
%             Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,daysToReset),'ascend');
            
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            
            eventTimeIdx(1) = find(timeStep == daysToReset);
            eventTimeIdx(2) = find(timeStep == maturity);
            
%             for i= scheduleSize:-1:lastAliveExerciseIdx
%                 idx = find(timeStep == maturity);
%                 eventTimeIdx(i) = min(idx);
%             end
            
            %% MC init 
            useQuasiRandomYN = eqCOMDupireSpotGF.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
            else
                rng('default');
                rng(0);
                
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           
           nextX = initX;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           relativeStrike =  vanillaParams.params('relativeStrike');
           
           detFwdReset    = eqCOMDupireSpotGF.FwdFactor(daysToReset);
           detFwdMaturity = eqCOMDupireSpotGF.FwdFactor(maturity);
           
           fwdRatio = detFwdMaturity/detFwdReset;
           
%            relativeStrike =  [0.5:0.1:1.5];
           
           reSetS = zeros(NMC,1);      
%            modelStates = eqCOMDupireSpotGF.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                if i== 1
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                else
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                end
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    
                    nextX = mcmcOut.nextX;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                % at startDate, we reset strike
                if i==1
                    comFwd = eqCOMDupireSpotGF.EQFwdMC(currentTime,nextX);
                    reSetS = comFwd;
                    
                end
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqCOMDupireSpotGF.EQFwdMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i)/reSetS(i) - relativeStrike*fwdRatio,0);
                    payoffStateB.cashflow(i) = max(comFwd(i)/reSetS(i) - relativeStrike*fwdRatio,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i)/reSetS(i) + relativeStrike*fwdRatio,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i)/reSetS(i) + relativeStrike*fwdRatio,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
%            df_ep = eqCOMDupireSpotGF.zeroCurve.DF(currentTime/365.0);
           df_ep = 1.0;
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture;
           out.fwdRatio = fwdRatio;
        end
        
        
        function out = computeVolKnockOutTargetOption1SMC(eqCOMDupireSpotGF,valueDate,volTargetOptionParams,numMethod)
           
            % model schedule generation
            dealStartDate = volTargetOptionParams.startDate;
            dealStartEventTime = DateDiff(dealStartDate,valueDate);
            expiryDate = volTargetOptionParams.endDate;
            dealEndEventTime = DateDiff(expiryDate,valueDate);
            
          %% firstSchedulestructuredCouponSchedule start
            % firstSchedule is a schedule of first 30 days with fixed participation ratio
            
            firstScheduleInt = volTargetOptionParams.params.volTargetInfo.firstScheduleInt;
            
            firstScheduleSize = size(firstScheduleInt,1);
            firstSchedule= struct;
            firstSchedule.scheduleSize = firstScheduleSize;
            
%             firstSchedule.eventType = volTargetOptionParams.params.volTargetInfo.eventType;
            firstSchedule.eventType = volTargetOptionParams.params.volTargetInfo.firstSchedule_eventType;
            
            % eventTime is endDate
            % payment date can be different from endDate
            
            % startTime,endTimeP should be included in timeStep Generation
            % with eventTime
            
            for i=1:firstSchedule.scheduleSize
                firstResetDate = H_Date(firstScheduleInt(i,1));
                firstStartDate = H_Date(firstScheduleInt(i,2));
                firstEndDate = H_Date(firstScheduleInt(i,3));
                firstPayDate = H_Date(firstScheduleInt(i,4));
                
                firstSchedule.dayCount(i) = firstEndDate.DateDiff(firstStartDate);
                firstSchedule.dayCountFraction(i) = firstSchedule.dayCount(i)/365.0; 
                
                firstEndDateP = firstEndDate.AddDate( -1 ,'day');
                
                firstSchedule.resetTime(i) = DateDiff(firstResetDate,valueDate);
                firstSchedule.startTime(i) = DateDiff(firstStartDate,valueDate);
                firstSchedule.endTimeP(i)  = DateDiff(firstEndDateP,valueDate);
                firstSchedule.endTime(i) = DateDiff(firstEndDate,valueDate);
                
                if strcmp(firstSchedule.eventType,'RESET')
                    firstSchedule.eventTime(i) = DateDiff(firstResetDate,valueDate);
                elseif strcmp(firstSchedule.eventType,'START')
                    firstSchedule.eventTime(i) = DateDiff(firstStartDate,valueDate);
                elseif strcmp(firstSchedule.eventType,'END')
                    firstSchedule.eventTime(i) = DateDiff(firstEndDate,valueDate);
                else % default is END : event happens at EndDate for Structuredfirst
                    firstSchedule.eventTime(i) = DateDiff(firstEndDate,valueDate);
                end
                firstSchedule.payTime(i) = DateDiff(firstPayDate,valueDate);
                
            end
            
            
%             tenorInverseFloater     = steepenerParams.params.structuredCouponInfo.tenorInverseFloater;
%             volTargetInfo.multiplier = 0.7;
%             volTargetInfo.volTarget = 0.1;
%             volTargetInfo.volPeriod = 30;
%             volTargetInfo.volPeriodParticipation = 0.5;
%             volTargetInfo.leverageCap = 1.0;

           
           %% firstSchedule end
           
%            %% call exercise event happens at the callExerciseDate
%            %% callable schedule start
%             callableScheduleInt = steepenerParams.params.callableInfo.callableScheduleInt;
%             callableScheduleSize = size(callableScheduleInt,1);
%             callableSchedule= struct;
%             for i=1:callableScheduleSize
%                 callExerciseDate = H_Date(callableScheduleInt(i,1));
%                 callPayDate = H_Date(callableScheduleInt(i,2));
%                 callableSchedule.eventTime(i) = DateDiff(callExerciseDate,valueDate);
%                 callableSchedule.payTime(i) = DateDiff(callPayDate,valueDate);
%                 
%                  callableSchedule.callPayment(i) = callableScheduleInt(i,3);
%             end
%             callableSchedule.scheduleSize = callableScheduleSize;
%            
%             isExercised = steepenerParams.params.callableInfo.isExercised;
%            %% callable schedule end
           
          %% swapFloatingCouponSchedule start
           % firstSchedule is a schedule of first 30 days with fixed participation ratio
              
            lastScheduleInt = volTargetOptionParams.params.volTargetInfo.lastScheduleInt;
            
            
            lastScheduleSize = size(lastScheduleInt,1);
            lastSchedule= struct;
            lastSchedule.scheduleSize = lastScheduleSize;
            
%             lastSchedule.eventType = volTargetOptionParams.params.volTargetInfo.eventType;
            lastSchedule.eventType = volTargetOptionParams.params.volTargetInfo.lastSchedule_eventType;
            
            % eventTime is endDate
            % payment date can be different from endDate
            
            % startTime,endTimeP should be included in timeStep Generation
            % with eventTime
            
            for i=1:lastSchedule.scheduleSize
                lastResetDate = H_Date(lastScheduleInt(i,1));
                lastStartDate = H_Date(lastScheduleInt(i,2));
                lastEndDate = H_Date(lastScheduleInt(i,3));
                lastPayDate = H_Date(lastScheduleInt(i,4));
                
                lastSchedule.dayCount(i) = lastEndDate.DateDiff(lastStartDate);
                lastSchedule.dayCountFraction(i) = lastSchedule.dayCount(i)/365.0; 
                
                lastEndDateP = lastEndDate.AddDate( -1 ,'day');
                
                lastSchedule.resetTime(i) = DateDiff(lastResetDate,valueDate);
                lastSchedule.startTime(i) = DateDiff(lastStartDate,valueDate);
                lastSchedule.endTimeP(i)  = DateDiff(lastEndDateP,valueDate);
                lastSchedule.endTime(i) = DateDiff(lastEndDate,valueDate);
                
                if strcmp(lastSchedule.eventType,'RESET')
                    lastSchedule.eventTime(i) = DateDiff(lastResetDate,valueDate);
                elseif strcmp(lastSchedule.eventType,'START')
                    lastSchedule.eventTime(i) = DateDiff(lastStartDate,valueDate);
                elseif strcmp(lastSchedule.eventType,'END')
                    lastSchedule.eventTime(i) = DateDiff(lastEndDate,valueDate);
                else % default is END : event happens at EndDate for Structuredfirst
                    lastSchedule.eventTime(i) = DateDiff(lastEndDate,valueDate);
                end
                lastSchedule.payTime(i) = DateDiff(lastPayDate,valueDate);
                
            end
            
          %% lastSchedule end
          
          %% eventTimeStep(pricing time Step) Generation start
            
            % eventTimeStep Generate
%             mcOneTimeStep = numMethod.mcOneTimeStep;
            
          %% eventTime from dealStartTime and dealEndTime
           eventTimeStep = dealStartEventTime;
           eventTimeStep = union(eventTimeStep,dealEndEventTime);
           
          %% eventTime From firstSchedule:eventTime(endTime) +
          
          %% eventTime From firstSchedule:eventTime
            eventTimeStep = union(eventTimeStep,firstSchedule.eventTime);
          %% eventTime From lastSchedule:eventTime
            eventTimeStep = union(eventTimeStep,lastSchedule.eventTime);  
            eventTimeStep = sort(eventTimeStep,'ascend');
            
            if dealStartEventTime < 0 
                dailyTimeSteps = [0:-1:dealStartEventTime];
                eventTimeStep = union(eventTimeStep,dailyTimeSteps);
            end
            
            eventTimeStep = sort(eventTimeStep,'ascend');
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= dealEndEventTime));
            eventTimeStep = union(eventTimeStep,volExpiry);
            
            eventTimeStep = sort(eventTimeStep,'ascend');
            
            % mc time steps Generate
            timeStepP = numMethod.mcOneTimeStep;
            dailyTimeSteps = [dealEndEventTime:-timeStepP:0]';
            dailyTimeSteps = [dailyTimeSteps;0];
            eventTimeStep = sort(union(eventTimeStep,dailyTimeSteps),'ascend');
            
            
          %% aliveTimeStep for mc path generation
            aliveTimeStep = eventTimeStep(eventTimeStep>=0);
            aliveTimeStep = sort(aliveTimeStep,'ascend');
            
            totalAliveTimeStepSize = length(aliveTimeStep);
            
          %% eventTimeStep Generation End
            
          %% numeraire info
            numMatTime = eventTimeStep(end);
            dfNumMat = eqCOMDupireSpotGF.zeroCurve.DF(numMatTime/365.0);

            numeraire.numMatTime = numMatTime;
            numeraire.dfNumMat = dfNumMat;
            
          %% pricing time Step Generation end
            
            % should we use eventTimeIdx as future only time stes?
            % In this case we better use more generic approach
            % so that all times steps are included 
            
            bbb= 0.0;
            
            
          %% MC init
            rng('default');
            rng(0);
            
            numOfFactors = eqCOMDupireSpotGF.numOfFactors;
            NMC = numMethod.pathSize; 
            MCTimeStep = totalAliveTimeStepSize -1; % nowDate (0) should be skipped
%             Z= randn(NMC/2,MCTimeStep);
            Z= randn(NMC/2,numOfFactors*MCTimeStep);
            Z=[Z;-Z];
            Z=Z';

            %TimeInversion
            sizeZ = size(Z,1);
            A = zeros(sizeZ,sizeZ);
            for i=1:sizeZ
                A(i,sizeZ + 1 -i) = 1;
            end
            Z = A*Z;

%                 U = Z';
            U = Z;

           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(numOfFactors,NMC);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           
%            initXIdx = ones(NMC,1)*Pricingidx;
           initXIdx = ones(NMC,numOfFactors)*Pricingidx;
           
           nextX = initX;
           
           nextXIdx = initXIdx;
           modelStatesSize = NMC;
        
           
          
            % EODFlag : if true then pricing as EndOfDate(cashflow on
           % valueDate wil be not included(already paid)
           % if false then pricing as Intraday ( cashflow on valueDate will 
           % be included)
           
           %EODFlag_Cashflow: Cashflow EOD Flag
           %EODFlag_Exercise: Exercise(Option) EOD Flag
           EODFlag_Cashflow = volTargetOptionParams.params.volTargetInfo.EODFlag_Cashflow;
           EODFlag_Exercise = volTargetOptionParams.params.volTargetInfo.EODFlag_Exercise;
           
          %% payoff init
           nominal = volTargetOptionParams.params.nominal;
           multiplier = volTargetOptionParams.params.volTargetInfo.multiplier;
           volTarget   = volTargetOptionParams.params.volTargetInfo.volTarget;
           volPeriod = volTargetOptionParams.params.volTargetInfo.volPeriod;
           volPeriodParticipationRate     = volTargetOptionParams.params.volTargetInfo.volPeriodParticipationRate;
           leverageCap     = volTargetOptionParams.params.volTargetInfo.leverageCap;
           
           %KnockOutOptionInfo
           KOFlag       = volTargetOptionParams.params.volTargetInfo.KOFlag;
           
           if KOFlag
               isKOFlag = 1;
           else
               isKOFlag = 0;
           end
           
           
           optionType   = volTargetOptionParams.params.volTargetInfo.optionType;
           optionStrike = volTargetOptionParams.params.volTargetInfo.optionStrike;
           basePrice    = volTargetOptionParams.params.volTargetInfo.basePrice;
           
           modelStatesSize = NMC;

           
          %% Define Pricing Columns
           % pricingColumns : Price  
           % we need volTargetIndex as state variables for storing 
           % volTargetIndex
           
           % for the cashflow generated pricing columns as pricerInfo
           % we do use pricerInfo Structure
           
         %% (global) state variable initialize  : these correspond to ColumnVal[t] in generic pricing deal description

            %% we don't need global state variable for this
            % DealStartDate + firstScheduleEnd + LastScheduleEnd
            totalScheduleSize = firstSchedule.scheduleSize + lastSchedule.scheduleSize + 1;
            firstScheduleSize = firstSchedule.scheduleSize;
            equityIndex1 = zeros(totalScheduleSize,modelStatesSize);
            
%             cachedModelStatesCoupon = zeros(structuredCouponSchedule.scheduleSize*numOfFactors,modelStatesSize);
           
          %%
          
          %% PricingColumnGenericCashflow
          %% a structure that has cashflows with cashflowNames
          %% for CMS AVG structured we have nonCall, nonCallB, callable
           
            %nonCall
            cashflowNames = {'priceOption','volTargetIndex'};
            cashflowSizeMap = containers.Map({'priceOption','volTargetIndex'},{1, ...
                                            1});
            
            cashflowInfo.cashflowNames = cashflowNames;
            cashflowInfo.cashflowSizeMap = cashflowSizeMap;
            cashflowInfo.pathSize = modelStatesSize;
            
            priceOption = PricingColumnInfoGenericCashflow(cashflowInfo);
            volTargetIndex = PricingColumnInfoGenericCashflow(cashflowInfo);
             
           
           % intermediate variables
           payoffStateA.cashflow = zeros(1,modelStatesSize);
           payoffStateA.cashflow_npv = zeros(1,modelStatesSize);
           
           % local Variables
           
           annualDays = 252; % 
           
           R2      = zeros(1,modelStatesSize);
           R2Alpha = zeros(1,modelStatesSize);
           
           R       = zeros(1,modelStatesSize);
           RAlpha  = zeros(1,modelStatesSize);
           
           volIdx     = ones(1,modelStatesSize)*100.0;
           alpha   = ones(1,modelStatesSize)*volPeriodParticipationRate;
           
           RLog    = zeros(1,modelStatesSize);
           histRLog = zeros(1,modelStatesSize);
           
           equityIdxPre = zeros(1,modelStatesSize);
           equityIdx = zeros(1,modelStatesSize);
           
           optionAlpha = zeros(1,modelStatesSize);
           optionSigma = zeros(1,modelStatesSize);
           
           
           isKO = ones(1,modelStatesSize)*isKOFlag;
           
%            alphaIdx = 1;
%            alphaTrace = zeros(1000,modelStatesSize);
%            alphaTrace(1,:) = alpha;
%            
%            volIdxTrace = zeros(1000,modelStatesSize);
%            volIdxTrace(1,:) = volIdx;
%            
%            optionSigmaTrace = zeros(1000,modelStatesSize);
%            optionAlphaTrace = zeros(1000,modelStatesSize);
%            
%            alphaIdx = alphaIdx + 1;
           
           %            alphaIdx = alphaIdx + 1;
           
%            eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTimeStep,nextX);
           
          %% Path Generation Forward
          %% Store path dependent variables for coupon calculation 
          %% Store state variables to be used for AMC Regression
           
           %payoff descrption update index
           currentTimeIdx = 1;
           %MC numMethodState update index
           aliveTimeIdx = 1;
           % currentTimeStep is update in for statement
%            for currentTimeStep = eventTimeStep(1):1:eventTimeStep(end)
           for idxT = 1:1:length(eventTimeStep)
                currentTimeStep = eventTimeStep(idxT);
                
                if idxT < length(eventTimeStep)
                    nextTimeStep = eventTimeStep(idxT+1);
                end
                
                % evaluate scripts 
                % evaluate stateVariables(stores)
                % evaluate expression per each pricing columns
                % at the end of the loop we induct forward
                % from left to right
                % fictional payoff script columns are
                % cumCoupon,nonCall,Callable
                
                        
                % find the current
                % if find return errors then?
                try
                    
                    % AtDate operation on dealStart
                    
                    idxDealStartEvent = find(currentTimeStep == dealStartEventTime);

                    if ~isempty(idxDealStartEvent)
                        eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
%                         equityIdxPre = eqFwd;
                        equityIndex1(1,:) = eqFwd;
                        
                    end


                 
                 %% firstSchedule event start
                   if strcmp(firstSchedule.eventType,'END')
                     %% if we raise inverseFloaterCouponEvent at EndDate then
                     %% we need to raise fixing event at resetDate and store fixed inverseFloatRate as stateVariables
                     %% and reference it at ENDDate
                        
                        idxFirstScheduleEvent = find(currentTimeStep == firstSchedule.eventTime);
                        if ~isempty(idxFirstScheduleEvent)
                            % now if we are at firstSchedule
                            % eventTime(=endDate)
                            % then we update equityIdx,equityIdxPre
                            eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
                            
                            equityIndex1(1+idxFirstScheduleEvent,:) = eqFwd;
                            
                            equityIdx = equityIndex1(1+idxFirstScheduleEvent,:);
                            equityIdxPre = equityIndex1(1+idxFirstScheduleEvent-1,:);
                            
                            RLog = log(equityIdx./equityIdxPre);
                            R2 = R2 + RLog.*RLog;
                            R  = R  + RLog;
%                             volIdx = volIdx.*(1.0 + alpha .* (equityIdx./equityIdxPre -1.0));
%                             alphaTrace(alphaIdx,:) = alpha;
%                             volIdxTrace(alphaIdx,:) = volIdx;
%                             alphaIdx = alphaIdx + 1;
                            
%                             equityIdxPre = equityIdx;
                        end
                   else
%                        error('not supported eventType')
                       disp('reset date event is not supported!')
                   end
                %% firstSchedule event end 
                  
                %% lastSchedule event end 
                   if strcmp(lastSchedule.eventType,'END')
                     %% if we raise swapFloatingCouponEvent at EndDate then
                        idxLastScheduleEvent = find(currentTimeStep == lastSchedule.eventTime);
                        if ~isempty(idxLastScheduleEvent)
                            
                            eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
                            equityIndex1(1+firstScheduleSize + idxLastScheduleEvent,:) = eqFwd;
                            equityIdx    = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent,:);
                            equityIdxPre = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent-1,:);
                            
                            RLog = log(equityIdx./equityIdxPre);
                            R  = R  + RLog;
                            R2 = R2 + RLog.*RLog;
                            
                            
                            
                            % trailing Return to be subtracted
                            histIdx = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent - volPeriod ,:);
                            histIdxPre = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent - volPeriod - 1 ,:);
                            
                            histRLog = log(histIdx./histIdxPre);
                            RAlpha  = RAlpha  + histRLog;
                            R2Alpha = R2Alpha + histRLog.*histRLog;
                            
                            
                            vaR = (R2 - R2Alpha) - (R - RAlpha).*(R - RAlpha)./volPeriod; 
                            optionSigma = sqrt(annualDays./volPeriod .* vaR);
%                             optionAlpha = min(leverageCap,volTarget./optionSigma);
%                             optionAlpha = volPeriodParticipationRate.* min(leverageCap,volTarget./optionSigma);
                            
                            
                            for idxhh = 1:modelStatesSize
                                if isKO(idxhh) || volTarget <= optionSigma(idxhh)
                                    isKO(idxhh) = 1.0;
                                end
                            end
                            
%                             volIdx = volIdx.*(1.0 + alpha .* (equityIdx./equityIdxPre -1.0));
                            
%                             alphaTrace(alphaIdx,:) = alpha;
%                             volIdxTrace(alphaIdx,:) = volIdx;
%                             optionSigmaTrace(alphaIdx,:) = optionSigma;
%                             optionAlphaTrace(alphaIdx,:) = optionAlpha;
%                             
%                             alphaIdx = alphaIdx + 1;
%                             equityIdxPre = equityIdx;
%                             alpha = optionAlpha;
                            
                        end    
                    else
%                        error('not supported eventType')
                       disp('reset date event is not supported!')
                   end
                    
                   
                   idxDealEndEvent = find(currentTimeStep == dealEndEventTime);

                    if ~isempty(idxDealEndEvent)
                        eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
                        
%                         optionValue = nominal * multiplier * max(volIdx./100.0 - 1.0,0.0);
                        
                        if strcmp(optionType,'Call')
                            optionValue = nominal * multiplier * max(eqFwd./basePrice - optionStrike,0.0).*(1.0 - isKO);
                        else
                            optionValue = nominal * multiplier * max(optionStrike - eqFwd./basePrice,0.0).*(1.0 - isKO);
                        end
                        
                        payoffStateA.cashflow = optionValue;

                     %% since we are paying floating CMS Coupon
%                      priceOption
%                      volTargetIndex

                        eodFlag = EODAdjust(EODFlag_Cashflow,currentTimeStep);
                        payoffStateA.cashflow = payoffStateA.cashflow * eodFlag;

                        payTime = dealEndEventTime;

                        %process payoff cashflow 
                        priceOption.ProcessAddPayoff(eqCOMDupireSpotGF,currentTimeStep,payTime,numeraire,nextX, ...
                                                payoffStateA.cashflow,'priceOption',1);
                                            
%                         volTargetIndex.ProcessAddPayoff(eqCOMDupireSpotGF,currentTimeStep,payTime,numeraire,nextX, ...
%                                                 volIdx,'volTargetIndex',1);  
                        
                        ccc = 0.0;
                                                
%                         eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(currentTimeStep,nextX);
%                         equityIdxPre = eqFwd;
%                         equityIndex1(1,:) = eqFwd;
                        
                    end
                   
                    % if currentTimeSteps is today or future then inductMCForward
                    if currentTimeStep >= 0 && currentTimeStep < eventTimeStep(end)
                        mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,currentTimeStep,nextTimeStep,...
                                    nextX,U(numOfFactors*(aliveTimeIdx-1)+1:numOfFactors*aliveTimeIdx,:));
                        nextX = mcmcOut.nextX;
                        
%                         mcmcOut   = inductMCForwardNew(ck1F,currentTimeStep,nextTimeStep,...
%                                     nextX,U(numOfFactors*(aliveTimeIdx-1)+1:numOfFactors*aliveTimeIdx,:));
%                         nextX = mcmcOut.nextX;
                        %MC numMethodState update
                        aliveTimeIdx = aliveTimeIdx + 1;
                    end
                    
                    currentTimeIdx = currentTimeIdx +1;
                    
                catch exception
                    throw(exception)
                end
                
                
           end
           
          %% Forward Induction End
           
          ccc = 0.0;
          
          %% Finalize output
           priceOption.npv = mean(priceOption.payoff);
%            volTargetIndex.npv = mean(volTargetIndex.payoff);
           
           %forward
           out.priceOption = priceOption; 
           %backward
%            out.volTargetIndex = volTargetIndex; 
%            out.optionSigmaTrace = optionSigmaTrace;
%            out.optionAlphaTrace = optionAlphaTrace;
           
           out.eventTimeStep = eventTimeStep';
%            out.alphaTrace = alphaTrace;
%            out.volIdxTrace = volIdxTrace;
           
           
        end
        
        function out = computeVolTargetOption1SMC2(eqCOMDupireSpotGF,valueDate,volTargetOptionParams,numMethod)
           
            % model schedule generation
            dealStartDate = volTargetOptionParams.startDate;
            dealStartEventTime = DateDiff(dealStartDate,valueDate);
            expiryDate = volTargetOptionParams.endDate;
            dealEndEventTime = DateDiff(expiryDate,valueDate);
            
          %% firstSchedulestructuredCouponSchedule start
            % firstSchedule is a schedule of first 30 days with fixed participation ratio
            
            firstScheduleInt = volTargetOptionParams.params.volTargetInfo.firstScheduleInt;
            
            firstScheduleSize = size(firstScheduleInt,1);
            firstSchedule= struct;
            firstSchedule.scheduleSize = firstScheduleSize;
            
%             firstSchedule.eventType = volTargetOptionParams.params.volTargetInfo.eventType;
            firstSchedule.eventType = volTargetOptionParams.params.volTargetInfo.firstSchedule_eventType;
            
            % eventTime is endDate
            % payment date can be different from endDate
            
            % startTime,endTimeP should be included in timeStep Generation
            % with eventTime
            
            for i=1:firstSchedule.scheduleSize
                firstResetDate = H_Date(firstScheduleInt(i,1));
                firstStartDate = H_Date(firstScheduleInt(i,2));
                firstEndDate = H_Date(firstScheduleInt(i,3));
                firstPayDate = H_Date(firstScheduleInt(i,4));
                
                firstSchedule.dayCount(i) = firstEndDate.DateDiff(firstStartDate);
                firstSchedule.dayCountFraction(i) = firstSchedule.dayCount(i)/365.0; 
                
                firstEndDateP = firstEndDate.AddDate( -1 ,'day');
                
                firstSchedule.resetTime(i) = DateDiff(firstResetDate,valueDate);
                firstSchedule.startTime(i) = DateDiff(firstStartDate,valueDate);
                firstSchedule.endTimeP(i)  = DateDiff(firstEndDateP,valueDate);
                firstSchedule.endTime(i) = DateDiff(firstEndDate,valueDate);
                
                if strcmp(firstSchedule.eventType,'RESET')
                    firstSchedule.eventTime(i) = DateDiff(firstResetDate,valueDate);
                elseif strcmp(firstSchedule.eventType,'START')
                    firstSchedule.eventTime(i) = DateDiff(firstStartDate,valueDate);
                elseif strcmp(firstSchedule.eventType,'END')
                    firstSchedule.eventTime(i) = DateDiff(firstEndDate,valueDate);
                else % default is END : event happens at EndDate for Structuredfirst
                    firstSchedule.eventTime(i) = DateDiff(firstEndDate,valueDate);
                end
                firstSchedule.payTime(i) = DateDiff(firstPayDate,valueDate);
                
            end
            
            
%             tenorInverseFloater     = steepenerParams.params.structuredCouponInfo.tenorInverseFloater;
%             volTargetInfo.multiplier = 0.7;
%             volTargetInfo.volTarget = 0.1;
%             volTargetInfo.volPeriod = 30;
%             volTargetInfo.volPeriodParticipation = 0.5;
%             volTargetInfo.leverageCap = 1.0;

           
           %% firstSchedule end
           
%            %% call exercise event happens at the callExerciseDate
%            %% callable schedule start
%             callableScheduleInt = steepenerParams.params.callableInfo.callableScheduleInt;
%             callableScheduleSize = size(callableScheduleInt,1);
%             callableSchedule= struct;
%             for i=1:callableScheduleSize
%                 callExerciseDate = H_Date(callableScheduleInt(i,1));
%                 callPayDate = H_Date(callableScheduleInt(i,2));
%                 callableSchedule.eventTime(i) = DateDiff(callExerciseDate,valueDate);
%                 callableSchedule.payTime(i) = DateDiff(callPayDate,valueDate);
%                 
%                  callableSchedule.callPayment(i) = callableScheduleInt(i,3);
%             end
%             callableSchedule.scheduleSize = callableScheduleSize;
%            
%             isExercised = steepenerParams.params.callableInfo.isExercised;
%            %% callable schedule end
           
          %% swapFloatingCouponSchedule start
           % firstSchedule is a schedule of first 30 days with fixed participation ratio
              
            lastScheduleInt = volTargetOptionParams.params.volTargetInfo.lastScheduleInt;
            
            
            lastScheduleSize = size(lastScheduleInt,1);
            lastSchedule= struct;
            lastSchedule.scheduleSize = lastScheduleSize;
            
%             lastSchedule.eventType = volTargetOptionParams.params.volTargetInfo.eventType;
            lastSchedule.eventType = volTargetOptionParams.params.volTargetInfo.lastSchedule_eventType;
            
            % eventTime is endDate
            % payment date can be different from endDate
            
            % startTime,endTimeP should be included in timeStep Generation
            % with eventTime
            
            for i=1:lastSchedule.scheduleSize
                lastResetDate = H_Date(lastScheduleInt(i,1));
                lastStartDate = H_Date(lastScheduleInt(i,2));
                lastEndDate = H_Date(lastScheduleInt(i,3));
                lastPayDate = H_Date(lastScheduleInt(i,4));
                
                lastSchedule.dayCount(i) = lastEndDate.DateDiff(lastStartDate);
                lastSchedule.dayCountFraction(i) = lastSchedule.dayCount(i)/365.0; 
                
                lastEndDateP = lastEndDate.AddDate( -1 ,'day');
                
                lastSchedule.resetTime(i) = DateDiff(lastResetDate,valueDate);
                lastSchedule.startTime(i) = DateDiff(lastStartDate,valueDate);
                lastSchedule.endTimeP(i)  = DateDiff(lastEndDateP,valueDate);
                lastSchedule.endTime(i) = DateDiff(lastEndDate,valueDate);
                
                if strcmp(lastSchedule.eventType,'RESET')
                    lastSchedule.eventTime(i) = DateDiff(lastResetDate,valueDate);
                elseif strcmp(lastSchedule.eventType,'START')
                    lastSchedule.eventTime(i) = DateDiff(lastStartDate,valueDate);
                elseif strcmp(lastSchedule.eventType,'END')
                    lastSchedule.eventTime(i) = DateDiff(lastEndDate,valueDate);
                else % default is END : event happens at EndDate for Structuredfirst
                    lastSchedule.eventTime(i) = DateDiff(lastEndDate,valueDate);
                end
                lastSchedule.payTime(i) = DateDiff(lastPayDate,valueDate);
                
            end
            
          %% lastSchedule end
          
          %% eventTimeStep(pricing time Step) Generation start
            
            % eventTimeStep Generate
%             mcOneTimeStep = numMethod.mcOneTimeStep;
            
          %% eventTime from dealStartTime and dealEndTime
           eventTimeStep = dealStartEventTime;
           eventTimeStep = union(eventTimeStep,dealEndEventTime);
           
          %% eventTime From firstSchedule:eventTime(endTime) +
          
          %% eventTime From firstSchedule:eventTime
            eventTimeStep = union(eventTimeStep,firstSchedule.eventTime);
          %% eventTime From lastSchedule:eventTime
            eventTimeStep = union(eventTimeStep,lastSchedule.eventTime);  
            eventTimeStep = sort(eventTimeStep,'ascend');
            
            if dealStartEventTime < 0 
                dailyTimeSteps = [0:-1:dealStartEventTime];
                eventTimeStep = union(eventTimeStep,dailyTimeSteps);
            end
            
            eventTimeStep = sort(eventTimeStep,'ascend');
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= dealEndEventTime));
            eventTimeStep = union(eventTimeStep,volExpiry);
            
            eventTimeStep = sort(eventTimeStep,'ascend');
            
            % mc time steps Generate
            timeStepP = numMethod.mcOneTimeStep;
            dailyTimeSteps = [dealEndEventTime:-timeStepP:0]';
            dailyTimeSteps = [dailyTimeSteps;0];
            eventTimeStep = sort(union(eventTimeStep,dailyTimeSteps),'ascend');
            
            
          %% aliveTimeStep for mc path generation
            aliveTimeStep = eventTimeStep(eventTimeStep>=0);
            aliveTimeStep = sort(aliveTimeStep,'ascend');
            
            totalAliveTimeStepSize = length(aliveTimeStep);
            
          %% eventTimeStep Generation End
            
          %% numeraire info
            numMatTime = eventTimeStep(end);
            dfNumMat = eqCOMDupireSpotGF.zeroCurve.DF(numMatTime/365.0);

            numeraire.numMatTime = numMatTime;
            numeraire.dfNumMat = dfNumMat;
            
          %% pricing time Step Generation end
            
            % should we use eventTimeIdx as future only time stes?
            % In this case we better use more generic approach
            % so that all times steps are included 
            
            bbb= 0.0;
            
            
          %% MC init
            rng('default');
            rng(0);
            
            numOfFactors = eqCOMDupireSpotGF.numOfFactors;
            NMC = numMethod.pathSize; 
            MCTimeStep = totalAliveTimeStepSize -1; % nowDate (0) should be skipped
%             Z= randn(NMC/2,MCTimeStep);
            Z= randn(NMC/2,numOfFactors*MCTimeStep);
            Z=[Z;-Z];
            Z=Z';

            %TimeInversion
            sizeZ = size(Z,1);
            A = zeros(sizeZ,sizeZ);
            for i=1:sizeZ
                A(i,sizeZ + 1 -i) = 1;
            end
            Z = A*Z;

%                 U = Z';
            U = Z;

           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(numOfFactors,NMC);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           
%            initXIdx = ones(NMC,1)*Pricingidx;
           initXIdx = ones(NMC,numOfFactors)*Pricingidx;
           
           nextX = initX;
           
           nextXIdx = initXIdx;
           modelStatesSize = NMC;
        
           
          
            % EODFlag : if true then pricing as EndOfDate(cashflow on
           % valueDate wil be not included(already paid)
           % if false then pricing as Intraday ( cashflow on valueDate will 
           % be included)
           
           %EODFlag_Cashflow: Cashflow EOD Flag
           %EODFlag_Exercise: Exercise(Option) EOD Flag
           EODFlag_Cashflow = volTargetOptionParams.params.volTargetInfo.EODFlag_Cashflow;
           EODFlag_Exercise = volTargetOptionParams.params.volTargetInfo.EODFlag_Exercise;
           
          %% payoff init
           nominal = volTargetOptionParams.params.nominal;
           multiplier = volTargetOptionParams.params.volTargetInfo.multiplier;
           volTarget   = volTargetOptionParams.params.volTargetInfo.volTarget;
           volPeriod = volTargetOptionParams.params.volTargetInfo.volPeriod;
           volPeriodParticipationRate     = volTargetOptionParams.params.volTargetInfo.volPeriodParticipationRate;
           leverageCap     = volTargetOptionParams.params.volTargetInfo.leverageCap;
           
           modelStatesSize = NMC;

           
          %% Define Pricing Columns
           % pricingColumns : Price  
           % we need volTargetIndex as state variables for storing 
           % volTargetIndex
           
           % for the cashflow generated pricing columns as pricerInfo
           % we do use pricerInfo Structure
           
         %% (global) state variable initialize  : these correspond to ColumnVal[t] in generic pricing deal description

            %% we don't need global state variable for this
            % DealStartDate + firstScheduleEnd + LastScheduleEnd
            totalScheduleSize = firstSchedule.scheduleSize + lastSchedule.scheduleSize + 1;
            firstScheduleSize = firstSchedule.scheduleSize;
            equityIndex1 = zeros(totalScheduleSize,modelStatesSize);
            volIdxCache = zeros(totalScheduleSize,modelStatesSize);
            
%             cachedModelStatesCoupon = zeros(structuredCouponSchedule.scheduleSize*numOfFactors,modelStatesSize);
           
          %%
          
          %% PricingColumnGenericCashflow
          %% a structure that has cashflows with cashflowNames
          %% for CMS AVG structured we have nonCall, nonCallB, callable
           
            %nonCall
            cashflowNames = {'priceOption','volTargetIndex'};
            cashflowSizeMap = containers.Map({'priceOption','volTargetIndex'},{1, ...
                                            1});
            
            cashflowInfo.cashflowNames = cashflowNames;
            cashflowInfo.cashflowSizeMap = cashflowSizeMap;
            cashflowInfo.pathSize = modelStatesSize;
            
            priceOption = PricingColumnInfoGenericCashflow(cashflowInfo);
            volTargetIndex = PricingColumnInfoGenericCashflow(cashflowInfo);
             
           
           % intermediate variables
           payoffStateA.cashflow = zeros(1,modelStatesSize);
           payoffStateA.cashflow_npv = zeros(1,modelStatesSize);
           
           % local Variables
           
           annualDays = 252; % 
           
           R2      = zeros(1,modelStatesSize);
           R2Alpha = zeros(1,modelStatesSize);
           
           R       = zeros(1,modelStatesSize);
           RAlpha  = zeros(1,modelStatesSize);
           
           volIdx     = ones(1,modelStatesSize)*100.0;
           alpha   = ones(1,modelStatesSize)*volPeriodParticipationRate;
           
           RLog    = zeros(1,modelStatesSize);
           histRLog = zeros(1,modelStatesSize);
           
           equityIdxPre = zeros(1,modelStatesSize);
           equityIdx = zeros(1,modelStatesSize);
           
           optionAlpha = zeros(1,modelStatesSize);
           optionSigma = zeros(1,modelStatesSize);
           
%            alphaIdx = 1;
%            alphaTrace = zeros(1000,modelStatesSize);
%            alphaTrace(1,:) = alpha;
%            
%            volIdxTrace = zeros(1000,modelStatesSize);
%            volIdxTrace(1,:) = volIdx;
%            
%            optionSigmaTrace = zeros(1000,modelStatesSize);
%            optionAlphaTrace = zeros(1000,modelStatesSize);
%            
%            alphaIdx = alphaIdx + 1;
           
           %            alphaIdx = alphaIdx + 1;
           
%            eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTimeStep,nextX);
           
          %% Path Generation Forward
          %% Store path dependent variables for coupon calculation 
          %% Store state variables to be used for AMC Regression
           
           %payoff descrption update index
           currentTimeIdx = 1;
           %MC numMethodState update index
           aliveTimeIdx = 1;
           % currentTimeStep is update in for statement
%            for currentTimeStep = eventTimeStep(1):1:eventTimeStep(end)
           for idxT = 1:1:length(eventTimeStep)
                currentTimeStep = eventTimeStep(idxT);
                
                if idxT < length(eventTimeStep)
                    nextTimeStep = eventTimeStep(idxT+1);
                end
                
                % evaluate scripts 
                % evaluate stateVariables(stores)
                % evaluate expression per each pricing columns
                % at the end of the loop we induct forward
                % from left to right
                % fictional payoff script columns are
                % cumCoupon,nonCall,Callable
                
                        
                % find the current
                % if find return errors then?
                try
                    
                    % AtDate operation on dealStart
                    
                    idxDealStartEvent = find(currentTimeStep == dealStartEventTime);

                    if ~isempty(idxDealStartEvent)
                        eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
%                         equityIdxPre = eqFwd;
                        equityIndex1(1,:) = eqFwd;
                        volIdxCache(1,:) = volIdx;
                    end


                 
                 %% firstSchedule event start
                   if strcmp(firstSchedule.eventType,'END')
                     %% if we raise inverseFloaterCouponEvent at EndDate then
                     %% we need to raise fixing event at resetDate and store fixed inverseFloatRate as stateVariables
                     %% and reference it at ENDDate
                        
                        idxFirstScheduleEvent = find(currentTimeStep == firstSchedule.eventTime);
                        if ~isempty(idxFirstScheduleEvent)
                            % now if we are at firstSchedule
                            % eventTime(=endDate)
                            % then we update equityIdx,equityIdxPre
                            eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
                            
                            equityIndex1(1+idxFirstScheduleEvent,:) = eqFwd;
                            
                            equityIdx = equityIndex1(1+idxFirstScheduleEvent,:);
                            equityIdxPre = equityIndex1(1+idxFirstScheduleEvent-1,:);
                            
                            RLog = log(equityIdx./equityIdxPre);
                            R2 = R2 + RLog.*RLog;
                            R  = R  + RLog;
                            volIdx = volIdx.*(1.0 + alpha .* (equityIdx./equityIdxPre -1.0));
                            volIdxCache(1+idxFirstScheduleEvent,:) = volIdx;
                            
%                             alphaTrace(alphaIdx,:) = alpha;
%                             volIdxTrace(alphaIdx,:) = volIdx;
%                             alphaIdx = alphaIdx + 1;
                            
%                             equityIdxPre = equityIdx;
                        end
                   else
%                        error('not supported eventType')
                       disp('reset date event is not supported!')
                   end
                %% firstSchedule event end 
                  
                %% lastSchedule event end 
                   if strcmp(lastSchedule.eventType,'END')
                     %% if we raise swapFloatingCouponEvent at EndDate then
                        idxLastScheduleEvent = find(currentTimeStep == lastSchedule.eventTime);
                        if ~isempty(idxLastScheduleEvent)
                            
                            eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
                            equityIndex1(1+firstScheduleSize + idxLastScheduleEvent,:) = eqFwd;
                            equityIdx    = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent,:);
                            equityIdxPre = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent-1,:);
                            
                            RLog = log(equityIdx./equityIdxPre);
                            R  = R  + RLog;
                            R2 = R2 + RLog.*RLog;
                            
                            
                            
                            % trailing Return to be subtracted
                            histIdx = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent - volPeriod ,:);
                            histIdxPre = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent - volPeriod - 1 ,:);
                            
                            histRLog = log(histIdx./histIdxPre);
                            RAlpha  = RAlpha  + histRLog;
                            R2Alpha = R2Alpha + histRLog.*histRLog;
                            
                            
                            vaR = (R2 - R2Alpha) - (R - RAlpha).*(R - RAlpha)./volPeriod; 
                            optionSigma = sqrt(annualDays./volPeriod .* vaR);
%                             optionAlpha = min(leverageCap,volTarget./optionSigma);
                            optionAlpha = volPeriodParticipationRate.* min(leverageCap,volTarget./optionSigma);
                            
                            
                            
                            volIdx = volIdx.*(1.0 + alpha .* (equityIdx./equityIdxPre -1.0));
                            volIdxCache(1+firstScheduleSize + idxLastScheduleEvent,:) = volIdx;
                            
%                             alphaTrace(alphaIdx,:) = alpha;
%                             volIdxTrace(alphaIdx,:) = volIdx;
%                             optionSigmaTrace(alphaIdx,:) = optionSigma;
%                             optionAlphaTrace(alphaIdx,:) = optionAlpha;
%                             
%                             alphaIdx = alphaIdx + 1;
%                             equityIdxPre = equityIdx;
                            alpha = optionAlpha;
                            
                        end    
                    else
%                        error('not supported eventType')
                       disp('reset date event is not supported!')
                   end
                    
                   
                   idxDealEndEvent = find(currentTimeStep == dealEndEventTime);

                    if ~isempty(idxDealEndEvent)
                        
                        optionValue = nominal * multiplier * max(volIdx./100.0 - 1.0,0.0);
                        
                        payoffStateA.cashflow = optionValue;

                     %% since we are paying floating CMS Coupon
%                      priceOption
%                      volTargetIndex

                        eodFlag = EODAdjust(EODFlag_Cashflow,currentTimeStep);
                        payoffStateA.cashflow = payoffStateA.cashflow * eodFlag;

                        payTime = dealEndEventTime;

                        %process payoff cashflow 
                        priceOption.ProcessAddPayoff(eqCOMDupireSpotGF,currentTimeStep,payTime,numeraire,nextX, ...
                                                payoffStateA.cashflow,'priceOption',1);
                                            
                        volTargetIndex.ProcessAddPayoff(eqCOMDupireSpotGF,currentTimeStep,payTime,numeraire,nextX, ...
                                                volIdx,'volTargetIndex',1);  
                        
                        ccc = 0.0;
                                                
%                         eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(currentTimeStep,nextX);
%                         equityIdxPre = eqFwd;
%                         equityIndex1(1,:) = eqFwd;
                        
                    end
                   
                    % if currentTimeSteps is today or future then inductMCForward
                    if currentTimeStep >= 0 && currentTimeStep < eventTimeStep(end)
                        mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,currentTimeStep,nextTimeStep,...
                                    nextX,U(numOfFactors*(aliveTimeIdx-1)+1:numOfFactors*aliveTimeIdx,:));
                        nextX = mcmcOut.nextX;
                        
%                         mcmcOut   = inductMCForwardNew(ck1F,currentTimeStep,nextTimeStep,...
%                                     nextX,U(numOfFactors*(aliveTimeIdx-1)+1:numOfFactors*aliveTimeIdx,:));
%                         nextX = mcmcOut.nextX;
                        %MC numMethodState update
                        aliveTimeIdx = aliveTimeIdx + 1;
                    end
                    
                    currentTimeIdx = currentTimeIdx +1;
                    
                catch exception
                    throw(exception)
                end
                
                
           end
           
          %% Forward Induction End
           
          ccc = 0.0;
          
          %% Finalize output
           priceOption.npv = mean(priceOption.payoff);
           volTargetIndex.npv = mean(volTargetIndex.payoff);
           
           %forward
           out.priceOption = priceOption; 
           %backward
           out.volTargetIndex = volTargetIndex; 
%            out.optionSigmaTrace = optionSigmaTrace;
%            out.optionAlphaTrace = optionAlphaTrace;
           
           out.eventTimeStep = eventTimeStep';
           out.equityIndex1 = equityIndex1;
           out.volIdxCache = volIdxCache;
           
%            out.alphaTrace = alphaTrace;
%            out.volIdxTrace = volIdxTrace;
           
           
        end
        
        function out = computeVolTargetOption1SMC(eqCOMDupireSpotGF,valueDate,volTargetOptionParams,numMethod)
           
            % model schedule generation
            dealStartDate = volTargetOptionParams.startDate;
            dealStartEventTime = DateDiff(dealStartDate,valueDate);
            expiryDate = volTargetOptionParams.endDate;
            dealEndEventTime = DateDiff(expiryDate,valueDate);
            
          %% firstSchedulestructuredCouponSchedule start
            % firstSchedule is a schedule of first 30 days with fixed participation ratio
            
            firstScheduleInt = volTargetOptionParams.params.volTargetInfo.firstScheduleInt;
            
            firstScheduleSize = size(firstScheduleInt,1);
            firstSchedule= struct;
            firstSchedule.scheduleSize = firstScheduleSize;
            
%             firstSchedule.eventType = volTargetOptionParams.params.volTargetInfo.eventType;
            firstSchedule.eventType = volTargetOptionParams.params.volTargetInfo.firstSchedule_eventType;
            
            % eventTime is endDate
            % payment date can be different from endDate
            
            % startTime,endTimeP should be included in timeStep Generation
            % with eventTime
            
            for i=1:firstSchedule.scheduleSize
                firstResetDate = H_Date(firstScheduleInt(i,1));
                firstStartDate = H_Date(firstScheduleInt(i,2));
                firstEndDate = H_Date(firstScheduleInt(i,3));
                firstPayDate = H_Date(firstScheduleInt(i,4));
                
                firstSchedule.dayCount(i) = firstEndDate.DateDiff(firstStartDate);
                firstSchedule.dayCountFraction(i) = firstSchedule.dayCount(i)/365.0; 
                
                firstEndDateP = firstEndDate.AddDate( -1 ,'day');
                
                firstSchedule.resetTime(i) = DateDiff(firstResetDate,valueDate);
                firstSchedule.startTime(i) = DateDiff(firstStartDate,valueDate);
                firstSchedule.endTimeP(i)  = DateDiff(firstEndDateP,valueDate);
                firstSchedule.endTime(i) = DateDiff(firstEndDate,valueDate);
                
                if strcmp(firstSchedule.eventType,'RESET')
                    firstSchedule.eventTime(i) = DateDiff(firstResetDate,valueDate);
                elseif strcmp(firstSchedule.eventType,'START')
                    firstSchedule.eventTime(i) = DateDiff(firstStartDate,valueDate);
                elseif strcmp(firstSchedule.eventType,'END')
                    firstSchedule.eventTime(i) = DateDiff(firstEndDate,valueDate);
                else % default is END : event happens at EndDate for Structuredfirst
                    firstSchedule.eventTime(i) = DateDiff(firstEndDate,valueDate);
                end
                firstSchedule.payTime(i) = DateDiff(firstPayDate,valueDate);
                
            end
            
            
%             tenorInverseFloater     = steepenerParams.params.structuredCouponInfo.tenorInverseFloater;
%             volTargetInfo.multiplier = 0.7;
%             volTargetInfo.volTarget = 0.1;
%             volTargetInfo.volPeriod = 30;
%             volTargetInfo.volPeriodParticipation = 0.5;
%             volTargetInfo.leverageCap = 1.0;

           
           %% firstSchedule end
           
%            %% call exercise event happens at the callExerciseDate
%            %% callable schedule start
%             callableScheduleInt = steepenerParams.params.callableInfo.callableScheduleInt;
%             callableScheduleSize = size(callableScheduleInt,1);
%             callableSchedule= struct;
%             for i=1:callableScheduleSize
%                 callExerciseDate = H_Date(callableScheduleInt(i,1));
%                 callPayDate = H_Date(callableScheduleInt(i,2));
%                 callableSchedule.eventTime(i) = DateDiff(callExerciseDate,valueDate);
%                 callableSchedule.payTime(i) = DateDiff(callPayDate,valueDate);
%                 
%                  callableSchedule.callPayment(i) = callableScheduleInt(i,3);
%             end
%             callableSchedule.scheduleSize = callableScheduleSize;
%            
%             isExercised = steepenerParams.params.callableInfo.isExercised;
%            %% callable schedule end
           
          %% swapFloatingCouponSchedule start
           % firstSchedule is a schedule of first 30 days with fixed participation ratio
              
            lastScheduleInt = volTargetOptionParams.params.volTargetInfo.lastScheduleInt;
            
            
            lastScheduleSize = size(lastScheduleInt,1);
            lastSchedule= struct;
            lastSchedule.scheduleSize = lastScheduleSize;
            
%             lastSchedule.eventType = volTargetOptionParams.params.volTargetInfo.eventType;
            lastSchedule.eventType = volTargetOptionParams.params.volTargetInfo.lastSchedule_eventType;
            
            % eventTime is endDate
            % payment date can be different from endDate
            
            % startTime,endTimeP should be included in timeStep Generation
            % with eventTime
            
            for i=1:lastSchedule.scheduleSize
                lastResetDate = H_Date(lastScheduleInt(i,1));
                lastStartDate = H_Date(lastScheduleInt(i,2));
                lastEndDate = H_Date(lastScheduleInt(i,3));
                lastPayDate = H_Date(lastScheduleInt(i,4));
                
                lastSchedule.dayCount(i) = lastEndDate.DateDiff(lastStartDate);
                lastSchedule.dayCountFraction(i) = lastSchedule.dayCount(i)/365.0; 
                
                lastEndDateP = lastEndDate.AddDate( -1 ,'day');
                
                lastSchedule.resetTime(i) = DateDiff(lastResetDate,valueDate);
                lastSchedule.startTime(i) = DateDiff(lastStartDate,valueDate);
                lastSchedule.endTimeP(i)  = DateDiff(lastEndDateP,valueDate);
                lastSchedule.endTime(i) = DateDiff(lastEndDate,valueDate);
                
                if strcmp(lastSchedule.eventType,'RESET')
                    lastSchedule.eventTime(i) = DateDiff(lastResetDate,valueDate);
                elseif strcmp(lastSchedule.eventType,'START')
                    lastSchedule.eventTime(i) = DateDiff(lastStartDate,valueDate);
                elseif strcmp(lastSchedule.eventType,'END')
                    lastSchedule.eventTime(i) = DateDiff(lastEndDate,valueDate);
                else % default is END : event happens at EndDate for Structuredfirst
                    lastSchedule.eventTime(i) = DateDiff(lastEndDate,valueDate);
                end
                lastSchedule.payTime(i) = DateDiff(lastPayDate,valueDate);
                
            end
            
          %% lastSchedule end
          
          %% eventTimeStep(pricing time Step) Generation start
            
            % eventTimeStep Generate
%             mcOneTimeStep = numMethod.mcOneTimeStep;
            
          %% eventTime from dealStartTime and dealEndTime
           eventTimeStep = dealStartEventTime;
           eventTimeStep = union(eventTimeStep,dealEndEventTime);
           
          %% eventTime From firstSchedule:eventTime(endTime) +
          
          %% eventTime From firstSchedule:eventTime
            eventTimeStep = union(eventTimeStep,firstSchedule.eventTime);
          %% eventTime From lastSchedule:eventTime
            eventTimeStep = union(eventTimeStep,lastSchedule.eventTime);  
            eventTimeStep = sort(eventTimeStep,'ascend');
            
            if dealStartEventTime < 0 
                dailyTimeSteps = [0:-1:dealStartEventTime];
                eventTimeStep = union(eventTimeStep,dailyTimeSteps);
            end
            
            eventTimeStep = sort(eventTimeStep,'ascend');
            
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= dealEndEventTime));
            eventTimeStep = union(eventTimeStep,volExpiry);
            
            eventTimeStep = sort(eventTimeStep,'ascend');
            
            % mc time steps Generate
            timeStepP = numMethod.mcOneTimeStep;
            dailyTimeSteps = [dealEndEventTime:-timeStepP:0]';
            dailyTimeSteps = [dailyTimeSteps;0];
            eventTimeStep = sort(union(eventTimeStep,dailyTimeSteps),'ascend');
            
            
          %% aliveTimeStep for mc path generation
            aliveTimeStep = eventTimeStep(eventTimeStep>=0);
            aliveTimeStep = sort(aliveTimeStep,'ascend');
            
            totalAliveTimeStepSize = length(aliveTimeStep);
            
          %% eventTimeStep Generation End
            
          %% numeraire info
            numMatTime = eventTimeStep(end);
            dfNumMat = eqCOMDupireSpotGF.zeroCurve.DF(numMatTime/365.0);

            numeraire.numMatTime = numMatTime;
            numeraire.dfNumMat = dfNumMat;
            
          %% pricing time Step Generation end
            
            % should we use eventTimeIdx as future only time stes?
            % In this case we better use more generic approach
            % so that all times steps are included 
            
            bbb= 0.0;
            
            
          %% MC init
            rng('default');
            rng(0);
            
            numOfFactors = eqCOMDupireSpotGF.numOfFactors;
            NMC = numMethod.pathSize; 
            MCTimeStep = totalAliveTimeStepSize -1; % nowDate (0) should be skipped
%             Z= randn(NMC/2,MCTimeStep);
            Z= randn(NMC/2,numOfFactors*MCTimeStep);
            Z=[Z;-Z];
            Z=Z';

            %TimeInversion
            sizeZ = size(Z,1);
            A = zeros(sizeZ,sizeZ);
            for i=1:sizeZ
                A(i,sizeZ + 1 -i) = 1;
            end
            Z = A*Z;

%                 U = Z';
            U = Z;

           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(numOfFactors,NMC);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
           
%            initXIdx = ones(NMC,1)*Pricingidx;
           initXIdx = ones(NMC,numOfFactors)*Pricingidx;
           
           nextX = initX;
           
           nextXIdx = initXIdx;
           modelStatesSize = NMC;
        
           
          
            % EODFlag : if true then pricing as EndOfDate(cashflow on
           % valueDate wil be not included(already paid)
           % if false then pricing as Intraday ( cashflow on valueDate will 
           % be included)
           
           %EODFlag_Cashflow: Cashflow EOD Flag
           %EODFlag_Exercise: Exercise(Option) EOD Flag
           EODFlag_Cashflow = volTargetOptionParams.params.volTargetInfo.EODFlag_Cashflow;
           EODFlag_Exercise = volTargetOptionParams.params.volTargetInfo.EODFlag_Exercise;
           
          %% payoff init
           nominal = volTargetOptionParams.params.nominal;
           multiplier = volTargetOptionParams.params.volTargetInfo.multiplier;
           volTarget   = volTargetOptionParams.params.volTargetInfo.volTarget;
           volPeriod = volTargetOptionParams.params.volTargetInfo.volPeriod;
           volPeriodParticipationRate     = volTargetOptionParams.params.volTargetInfo.volPeriodParticipationRate;
           leverageCap     = volTargetOptionParams.params.volTargetInfo.leverageCap;
           
           modelStatesSize = NMC;

           
          %% Define Pricing Columns
           % pricingColumns : Price  
           % we need volTargetIndex as state variables for storing 
           % volTargetIndex
           
           % for the cashflow generated pricing columns as pricerInfo
           % we do use pricerInfo Structure
           
         %% (global) state variable initialize  : these correspond to ColumnVal[t] in generic pricing deal description

            %% we don't need global state variable for this
            % DealStartDate + firstScheduleEnd + LastScheduleEnd
            totalScheduleSize = firstSchedule.scheduleSize + lastSchedule.scheduleSize + 1;
            firstScheduleSize = firstSchedule.scheduleSize;
            equityIndex1 = zeros(totalScheduleSize,modelStatesSize);
            
%             cachedModelStatesCoupon = zeros(structuredCouponSchedule.scheduleSize*numOfFactors,modelStatesSize);
           
          %%
          
          %% PricingColumnGenericCashflow
          %% a structure that has cashflows with cashflowNames
          %% for CMS AVG structured we have nonCall, nonCallB, callable
           
            %nonCall
            cashflowNames = {'priceOption','volTargetIndex'};
            cashflowSizeMap = containers.Map({'priceOption','volTargetIndex'},{1, ...
                                            1});
            
            cashflowInfo.cashflowNames = cashflowNames;
            cashflowInfo.cashflowSizeMap = cashflowSizeMap;
            cashflowInfo.pathSize = modelStatesSize;
            
            priceOption = PricingColumnInfoGenericCashflow(cashflowInfo);
            volTargetIndex = PricingColumnInfoGenericCashflow(cashflowInfo);
             
           
           % intermediate variables
           payoffStateA.cashflow = zeros(1,modelStatesSize);
           payoffStateA.cashflow_npv = zeros(1,modelStatesSize);
           
           % local Variables
           
           annualDays = 252; % 
           
           R2      = zeros(1,modelStatesSize);
           R2Alpha = zeros(1,modelStatesSize);
           
           R       = zeros(1,modelStatesSize);
           RAlpha  = zeros(1,modelStatesSize);
           
           volIdx     = ones(1,modelStatesSize)*100.0;
           alpha   = ones(1,modelStatesSize)*volPeriodParticipationRate;
           
           RLog    = zeros(1,modelStatesSize);
           histRLog = zeros(1,modelStatesSize);
           
           equityIdxPre = zeros(1,modelStatesSize);
           equityIdx = zeros(1,modelStatesSize);
           
           optionAlpha = zeros(1,modelStatesSize);
           optionSigma = zeros(1,modelStatesSize);
           
           
%            eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTimeStep,nextX);
           
          %% Path Generation Forward
          %% Store path dependent variables for coupon calculation 
          %% Store state variables to be used for AMC Regression
           
           %payoff descrption update index
           currentTimeIdx = 1;
           %MC numMethodState update index
           aliveTimeIdx = 1;
           % currentTimeStep is update in for statement
%            for currentTimeStep = eventTimeStep(1):1:eventTimeStep(end)
           for idxT = 1:1:length(eventTimeStep)
                currentTimeStep = eventTimeStep(idxT);
                
                if idxT < length(eventTimeStep)
                    nextTimeStep = eventTimeStep(idxT+1);
                end
                
                % evaluate scripts 
                % evaluate stateVariables(stores)
                % evaluate expression per each pricing columns
                % at the end of the loop we induct forward
                % from left to right
                % fictional payoff script columns are
                % cumCoupon,nonCall,Callable
                
                        
                % find the current
                % if find return errors then?
                try
                    
                    % AtDate operation on dealStart
                    
                    idxDealStartEvent = find(currentTimeStep == dealStartEventTime);

                    if ~isempty(idxDealStartEvent)
                        eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
                        equityIdxPre = eqFwd;
                        equityIndex1(1,:) = eqFwd;
                        
                    end


                 
                 %% firstSchedule event start
                   if strcmp(firstSchedule.eventType,'END')
                     %% if we raise inverseFloaterCouponEvent at EndDate then
                     %% we need to raise fixing event at resetDate and store fixed inverseFloatRate as stateVariables
                     %% and reference it at ENDDate
                        
                        idxFirstScheduleEvent = find(currentTimeStep == firstSchedule.eventTime);
                        if ~isempty(idxFirstScheduleEvent)
                            % now if we are at firstSchedule
                            % eventTime(=endDate)
                            % then we update equityIdx,equityIdxPre
                            eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
                            equityIdx = eqFwd;
                            
                            equityIndex1(1+idxFirstScheduleEvent,:) = eqFwd;
                        
                            RLog = log(equityIdx./equityIdxPre);
                            R2 = R2 + RLog.*RLog;
                            R  = R  + RLog;
                            volIdx = volIdx.*(1.0 + alpha .* (equityIdx./equityIdxPre -1.0));
                            
                            equityIdxPre = equityIdx;
                        end
                   else
%                        error('not supported eventType')
                       disp('reset date event is not supported!')
                   end
                %% firstSchedule event end 
                  
                %% lastSchedule event end 
                   if strcmp(lastSchedule.eventType,'END')
                     %% if we raise swapFloatingCouponEvent at EndDate then
                        idxLastScheduleEvent = find(currentTimeStep == lastSchedule.eventTime);
                        if ~isempty(idxLastScheduleEvent)
                            
                            eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(valueDate,currentTimeStep,nextX);
                            equityIdx = eqFwd;
                            equityIndex1(1+firstScheduleSize + idxLastScheduleEvent,:) = eqFwd;
                            
                            RLog = log(equityIdx./equityIdxPre);
                            R  = R  + RLog;
                            R2 = R2 + RLog.*RLog;
                            
                            
                            
                            % trailing Return to be subtracted
                            histIdx = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent - volPeriod ,:);
                            histIdxPre = equityIndex1(1+firstScheduleSize + idxLastScheduleEvent - volPeriod - 1 ,:);
                            
                            histRLog = log(histIdx./histIdxPre);
                            RAlpha  = RAlpha  + histRLog;
                            R2Alpha = R2Alpha + histRLog.*histRLog;
                            
                            
                            vaR = (R2 - R2Alpha) - (R - RAlpha).*(R - RAlpha)./volPeriod; 
                            optionSigma = sqrt(annualDays./volPeriod .* vaR);
                            optionAlpha = min(leverageCap,volTarget./optionSigma);
                            
                            volIdx = volIdx.*(1.0 + alpha .* (equityIdx./equityIdxPre -1.0));
                            
                            equityIdxPre = equityIdx;
                            alpha = optionAlpha;
                            
                        end    
                    else
%                        error('not supported eventType')
                       disp('reset date event is not supported!')
                   end
                    
                   
                   idxDealEndEvent = find(currentTimeStep == dealEndEventTime);

                    if ~isempty(idxDealEndEvent)
                        
                        optionValue = nominal * multiplier * max(volIdx./100.0 - 1.0,0.0);
                        
                        payoffStateA.cashflow = optionValue;

                     %% since we are paying floating CMS Coupon
%                      priceOption
%                      volTargetIndex

                        eodFlag = EODAdjust(EODFlag_Cashflow,currentTimeStep);
                        payoffStateA.cashflow = payoffStateA.cashflow * eodFlag;

                        payTime = dealEndEventTime;

                        %process payoff cashflow 
                        priceOption.ProcessAddPayoff(eqCOMDupireSpotGF,currentTimeStep,payTime,numeraire,nextX, ...
                                                payoffStateA.cashflow,'priceOption',1);
                                            
                        volTargetIndex.ProcessAddPayoff(eqCOMDupireSpotGF,currentTimeStep,payTime,numeraire,nextX, ...
                                                volIdx,'volTargetIndex',1);  
                        
                        ccc = 0.0;
                                                
%                         eqFwd = eqCOMDupireSpotGF.EQSpotMCGeneric(currentTimeStep,nextX);
%                         equityIdxPre = eqFwd;
%                         equityIndex1(1,:) = eqFwd;
                        
                    end
                   
                    % if currentTimeSteps is today or future then inductMCForward
                    if currentTimeStep >= 0 && currentTimeStep < eventTimeStep(end)
                        mcmcOut = inductMCForwardNew(eqCOMDupireSpotGF,currentTimeStep,nextTimeStep,...
                                    nextX,U(numOfFactors*(aliveTimeIdx-1)+1:numOfFactors*aliveTimeIdx,:));
                        nextX = mcmcOut.nextX;
                        
%                         mcmcOut   = inductMCForwardNew(ck1F,currentTimeStep,nextTimeStep,...
%                                     nextX,U(numOfFactors*(aliveTimeIdx-1)+1:numOfFactors*aliveTimeIdx,:));
%                         nextX = mcmcOut.nextX;
                        %MC numMethodState update
                        aliveTimeIdx = aliveTimeIdx + 1;
                    end
                    
                    currentTimeIdx = currentTimeIdx +1;
                    
                catch exception
                    throw(exception)
                end
                
                
           end
           
          %% Forward Induction End
           
          ccc = 0.0;
          
          %% Finalize output
           priceOption.npv = mean(priceOption.payoff);
           volTargetIndex.npv = mean(volTargetIndex.payoff);
           
           %forward
           out.priceOption = priceOption; 
           %backward
           out.volTargetIndex = volTargetIndex; 
           
           out.eventTimeStep = eventTimeStep';
           
           
           
        end
        
        function out = computePutShortStrategy1SMCMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MCMC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                % first random numbers goes to the enddate..
                for i=1:size(U,2)
                    U(:,i) = U0(:,size(U,2)-(i-1));
                end
            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
           Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
           initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
           nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcmcOut   = inductMCMCForward(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,nextXIdx,U(:,idx),Ks);
                    nextX = mcmcOut.nextX;
                    nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMCMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMCMC(StrikeSim,nextXIdx, ...
                                                              timeStep(idx+1),timeStep(endTimeIdx+1));
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computePutShortStrategy1SMC(eqCOMDupireSpotGF,valueDate,putShortStrategyParams)
%             out =0;
            % model schedule generation
            scheduleInt = putShortStrategyParams.params('denominatorResetScheduleInt');
            scheduleSize = size(scheduleInt,1);
            resetSchedule=[];
            for i=1:scheduleSize
                resetSchedule.resetDate(i) = H_Date(scheduleInt(i,1));
                resetSchedule.days(i) = DateDiff(resetSchedule.resetDate(i),valueDate);
                resetSchedule.strike(i) = scheduleInt(i,2);
            end
            resetSchedule.scheduleSize = scheduleSize;
            
            expiryDate = putShortStrategyParams.endDate;
%             expiryDate = resetSchedule.resetEndDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredReset = 0;
            aliveReset = 0;
            expiry = eqCOMDupireSpotGF.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(putShortStrategyParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            
            % we include resetDates
            for i= 1:scheduleSize
                daysToExercise = resetSchedule.days(i);
                if daysToExercise <= 0
                    expiredReset = expiredReset +1;
                    continue;
                else
                    aliveReset = aliveReset + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveResetIdx = 1 + expiredReset;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            
            % we add endDate(maturity) to eventTimes
            
%           eventTimeIdx = zeros(scheduleSize,1);
            eventTimeIdx = zeros(scheduleSize+1,1);
            
            for i= scheduleSize:-1:lastAliveResetIdx
                idx = find(timeStep == resetSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
            %endDate
            idx = find(timeStep == maturity);
            eventTimeIdx(end) = idx;
            
          %% MC init 
            useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqCOMDupireSpotGF.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = 400;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Z= randn(NMC/2,MCTimeStep);
%                 Z= rand(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           
           %nested MC init
           nestedNMC = eqCOMDupireSpotGF.modelParams('nestedNMC'); 
           rng('default');
           rng(0);
           nestedMaxTimeStepsSize = eqCOMDupireSpotGF.modelParams('nestedMaxTimeStepsSize'); 
           nestedMCOneTimeStep = eqCOMDupireSpotGF.modelParams('nestedMCOneTimeStep');
           
           MCTimeStep = nestedMaxTimeStepsSize -1; % nowDate (0) should be skipped
           Z= randn(nestedNMC/2,MCTimeStep);
           Z=[Z;-Z];
           Z=Z';

           %TimeInversion
           sizeZ = size(Z,1);
           A = zeros(sizeZ,sizeZ);
           for i=1:sizeZ
               A(i,sizeZ + 1 -i) = 1;
           end
           Z = A*Z;

           nestedU = Z';
           %NestedU contains random number for nested monte carlo
           
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = lastAliveResetIdx ; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           
           nominal = putShortStrategyParams.params('nominal');
           basePrice = putShortStrategyParams.params('basePrice');
           lowerBarrier = putShortStrategyParams.params('lowerBarrier');
           
           callStrike = putShortStrategyParams.params('callStrike');
           gearing = putShortStrategyParams.params('gearing');
           
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           
           payoffInfo.callStrike = callStrike;
           payoffInfo.resetSchedule = resetSchedule;
           
           modelStatesSize = NMC;

           indexValue.npv = 0;
           indexValue.payoff = zeros(modelStatesSize,1);
           indexValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           indexValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           optionValue.npv = 0;
           optionValue.payoff = zeros(modelStatesSize,1);
           optionValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize+1);
           optionValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize+1);
           
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           indexSim = zeros(modelStatesSize,1);
           prevOpt = zeros(modelStatesSize,1);
           currentOpt = zeros(modelStatesSize,1);
           
           % get the valueDate index Fixing
           allFixings = putShortStrategyParams.params('allFixings');
           putShortStrategyIndexFixing = allFixings('PutShortStrategyIndex');
           pastIndex = putShortStrategyIndexFixing(StrDate(valueDate,'str'));
           
           % we find the last denominatorfixing
           KOSPI200Fixing = allFixings('KOSPI200');
           pastSFixing = KOSPI200Fixing(StrDate(resetSchedule.resetDate(lastAliveResetIdx-1),'str'));
           
           
           indexSim = pastIndex*ones(modelStatesSize,1);
           eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
          %% Path Generation Forward
           % scheduleSize -> scheduleSize +1 because of endDate
           for i=lastAliveResetIdx:1:scheduleSize + 1
                if i > lastAliveResetIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
                if i == lastAliveResetIdx
                    fixingS  = pastSFixing*ones(modelStatesSize,1);
                    StrikeSim = fixingS*resetSchedule.strike(i-1);
                end
                
%                 prevOTM = eqCOMDupireSpotGF.ComputePutOTMPrices(StrikeSim,nextXIdx, ...
%                                                               timeStep(startTimeIdx),timeStep(endTimeIdx+1));
                
                prevOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                              timeStep(startTimeIdx),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                                                          
                Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    mcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    nextX = mcOut.nextX;
                    
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    eqFwd = eqCOMDupireSpotGF.EQSpotMC(currentTime,nextX);
                    % after induction we evaluate option price at
                    % timeSteps(idx+1)
                    currOTM = eqCOMDupireSpotGF.ComputePutOTMPricesMC(StrikeSim,nextX, ...
                                                             timeStep(idx+1),timeStep(endTimeIdx+1),...
                                                              nestedU,nestedNMC,nestedMCOneTimeStep);
                
                    indexSim = eqCOMDupireSpotGF.UpdatePutShortIndex(indexSim,fixingS,prevOTM,currOTM,timeStep(idx),timeStep(idx+1));
                    prevOTM = currOTM;
                    % per each path check whether Barrier was breached 
%                     isKI = BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo);
                end
                
                fixingS = eqFwd;
                
                % reset update is only for resetSchedule
                if i <= scheduleSize
                    StrikeSim = fixingS*resetSchedule.strike(i);
                end
                
                if i== scheduleSize
                    ccc = 1.0;
                end
                indexValue.payoffStates.cashflow(:,currentNodeIdx) = indexSim;
                indexValue.payoffStates.cashflow_npv(:,currentNodeIdx) = indexSim;
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = eqFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = eqFwd ;
                nMFuture.payoff = eqFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
           
           indexValue.payoff = indexValue.payoffStates.cashflow(:,end);
           
           dfOption = eqCOMDupireSpotGF.zeroCurve.DF(maturity/365.0);
           optionValue.payoff = dfOption*nominal*max(indexValue.payoff/basePrice - callStrike,0)*gearing;
           
%            for ii=1:length(modelStatesSize)
%                 optionValue.payoff(ii) = dfOption*nominal*max(indexValue.payoff(ii)/basePrice - callStrike,0)*gearing;
%            end

           indexValue.npv = mean(indexValue.payoff);
           optionValue.npv = mean(optionValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
           out.indexValue = indexValue;
           out.optionValue = optionValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardMCPerExpiry(eqCOMDupireSpotGF,idxNow,maturity,timeScheduleInfo,strikes,dZ,NMC,params)
            expiry = params.expiry;
            
            initX = ones(NMC,1);
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            %divide time interval into volExpiry
            for i=2:length(timeStep)
                startIdx = find(timeScheduleInfo.timeSchedule == timeStep(i-1));
                endIdx = find(timeScheduleInfo.timeSchedule == timeStep(i));
                dZStep = dZ(:,startIdx+1:endIdx);
                nextX = eqCOMDupireSpotGF.inductMCForward(timeStep(i-1),timeStep(i),startIdx,endIdx,timeScheduleInfo,nextX,dZStep,params);
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeForwardMCMCPerExpiry(eqCOMDupireSpotGF,maturity,strikes,U,NMC,params)
            expiry = params.expiry;
            Ks = params.Ks;
            initX = ones(NMC,1);
            initXIdx = ones(NMC,1)*params.Pricingidx;
            
            payoff = zeros(NMC,length(strikes));
            volExpiry = expiry(find(expiry <= maturity));
            volExpiry = [volExpiry; 0];
            timeStep = sort(union(volExpiry,maturity),'ascend');
            nextX = initX;
            nextXIdx = initXIdx;
            for i=2:length(timeStep)
                mcmcOut = eqCOMDupireSpotGF.inductMCMCForward(timeStep(i-1),timeStep(i),nextX,nextXIdx,U(:,i-1),Ks);
                nextX = mcmcOut.nextX;
                nextXIdx = mcmcOut.nextXIdx;
            end
            
            
            for j=1:length(strikes)
                if(strikes(j) <= 1)
                    payoff(:,j) = max(strikes(j) - nextX,0);
                else
                    payoff(:,j) = max(nextX - strikes(j),0);
                end
            end
            out = mean(payoff);
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            pdeOTMPrices =  zeros(length(expiry),length(strikes));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqCOMDupireSpotGF.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
        
        % compute forward mc(euler scheme) for 8*21 vanilla otm products
        % generate time steps from the enddate backwards 
        
        function out = computeForwardMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            % we generate the schedule from the enddate
            timeStepSize = params.mcOneTimeStep;
            MCTimeStep = round(expiry(length(expiry))/timeStepSize) +1; 
            dummyTimeSchedule = zeros(MCTimeStep,1);
            
            dummyN = 0;
            for i=1:MCTimeStep
                dummyTimeSchedule(i)= expiry(length(expiry)) -timeStepSize*(i-1);
                if dummyTimeSchedule(i) < 0
                    break;
                end
                dummyN = dummyN +1;
                
            end
            
            timeSchedule = zeros(dummyN,1);
            for i=1:dummyN
                timeSchedule(i)= dummyTimeSchedule(i);
            end
            
            volExpiry = [expiry; 0];
            
            newTimeSchedule = sort(union(volExpiry,timeSchedule),'ascend');
            
            dTSchedule = zeros(length(newTimeSchedule)-1,1);
            dTSchedule365 = zeros(length(newTimeSchedule)-1,1);
            for i=length(newTimeSchedule)-1:-1:1
                dTSchedule(i) = newTimeSchedule(i+1) - newTimeSchedule(i);
                dTSchedule365(i) = (newTimeSchedule(i+1) - newTimeSchedule(i))/365.0;
            end
            
            % find the vol expiry points
            
            volKnotIdx = zeros(length(expiry),1);
            for i=1:length(expiry)
                volKnotIdx(i) = find(newTimeSchedule==expiry(i));
                
            end
            
            timeScheduleInfo.timeSchedule = newTimeSchedule;
            timeScheduleInfo.dTSchedule = dTSchedule;
            timeScheduleInfo.dTSchedule365 = dTSchedule365;
            timeScheduleInfo.volKnowIdx = volKnotIdx;
            
            
            % schedule create end
%             NMC = params.NMC;
            NMC = eqCOMDupireSpotGF.modelParams('NMC'); 
%             Ps = sobolset(length(dTSchedule));
            
            Ps = sobolset(length(dTSchedule),'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            Q.reset;
            U = qrand(Q,NMC);
            dZ0 = zeros(size(U,1),size(U,2));
%             dZ = norminv(U);
            % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
            % generate random number from the end
            for i=1:size(U,1)
                for j=1:size(U,2)
                    dZ0(i,j) = r8_normal_01_cdf_inverse(U(i,j));
                end
            end
            
           % apply brownian bridge
           dZ1 = eqCOMDupireSpotGF.bbgenerator(dZ0);
           
           % first dZ is dummy , 0
           dZ = zeros(size(dZ1,1),size(dZ1,2) + 1);
           dZ(:,2) = dZ1(:,1);
           for i=3:size(dZ1,2)+1
                dZ(:,i) = dZ1(:,i-1) -  dZ1(:,i-2);
           end
           
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
%             mcOTMPrices =  zeros(length(expiry),length(strikes));
            
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCPerExpiry(i,expiry(i),timeScheduleInfo,strikePerExpiry,dZ,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        
        % compute forward mcmc(Markov Chain Monte Carlo scheme) for 8*21 vanilla otm products
        % generate time steps using only events date 
        
        function out = computeForwardMCMCOTMTotal(eqCOMDupireSpotGF,params)
            expiry = params.expiry;
            strikes = params.marketStrikes;
            
            %mc random number initialize
%             NMC = 2^14;
            NMC = params.NMC;
            
            MCTimeStep = length(expiry); % -1 because 0

            Ps = sobolset(MCTimeStep,'Skip',NMC);
%             Ps = scramble(Ps,'MatousekAffineOwen');
            Q = qrandstream(Ps);
            
            reset(Q);
            U0 = qrand(Q,NMC);
            U = zeros(NMC,MCTimeStep);
            
            % first random numbers goes to the enddate..
            for i=1:size(U,2)
                U(:,i) = U0(:,size(U,2)-(i-1));
            end            
            
            mcOTMPrices =  zeros(length(expiry),size(strikes,2));
            mcOTMPricesPerExpiry = zeros(1,size(strikes,2));
            for i=1:length(expiry)
                strikePerExpiry = strikes(i,:);
                mcOTMPricesPerExpiry = eqCOMDupireSpotGF.computeForwardMCMCPerExpiry(expiry(i),strikePerExpiry,U,NMC,params);
                for j=1:size(strikes,2)
                    mcOTMPrices(i,j) = mcOTMPricesPerExpiry(j);
                end
            end
            
            out = mcOTMPrices;
            
        end
        
        function out = computeForwardImpVolPerExpiry(eqCOMDupireSpotGF,maturity,strikes,params)
            
            expiry = params.expiry;
            lastP = zeros(1,length(params.Ks));
            lastP(params.Pricingidx) = 1.0;
            newP = zeros(1,length(params.Ks));
            
            
            idx = find(maturity <= expiry);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            
            %relevent volProxy
            volProxy = eqCOMDupireSpotGF.localVolSurface.volProxy(idxNow,:);
            
            %relevent probMesh and dTDays
            dTDays = 0;
            if idxNow~=1
                probMesh = eqCOMDupireSpotGF.localVolSurface.probMesh(idxNow-1,:);
                lastP = probMesh;
                dTDays = (maturity - expiry(idxNow-1));
            else % idxNow == 1
                dTDays = maturity;
            end
            
            
            ipos = eqCOMDupireSpotGF.localVolSurface.ipos(idxNow,:);
            Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            proxy = eqCOMDupireSpotGF.GetLocalVolFromProxy(volProxy,Ks,ipos,idxNow);

            %filling end
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);

            dK = Ks(2) - Ks(1);
            dT = dTDays/365.0;

            dK2 = dK*dK;
            for i=1:size
                a(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b(i) = 1 + dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                b_rg(i) = dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
                c(i) = -0.5*dT*proxy(i)*proxy(i)*Ks(i)*Ks(i)/dK2;
            end

            a(1) = 0;
            c(size) = 0;

            % absorbing boundary condition
            c(1) = 0;
            a(size) = 0;

            b(1) = 1;
            b(size) = 1;

            % to create tridiagonal matrix

            a1 = a(2:size);
            c1 = c(1:size-1);

            b_rg(1) = 0;
            b_rg(size) = 0;

            A_rg = full(gallery('tridiag',-a1*1.0/dT,-b_rg*1.0/dT,-c1*1.0/dT));
            A_exp1 = eqCOMDupireSpotGF.expmReghai(A_rg,dT);
            newP = lastP*A_exp1;
            
            
            impVol = zeros(1,length(strikes));
            
            %meshmatrixC(i,j) : max(x_i - k_j,0)
            %meshmatrixP(i,j) : max(-x_i + k_j,0)
            % payoff at maturity
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            strikeSize = length(strikes);
            meshC = zeros(modelXSize,strikeSize);
            meshP = zeros(modelXSize,strikeSize);
            
            for i=1:modelXSize
                for j=1:strikeSize
                    meshC(i,j) = max(modelX(i) - strikes(j),0);
                    meshP(i,j) = max(strikes(j) - modelX(i),0);
                end
            end
            
            cValue = zeros(1,strikeSize);
            pValue = zeros(1,strikeSize);
            
            impVolC = zeros(1,strikeSize);
            impVolP = zeros(1,strikeSize);
            impVol  = zeros(1,strikeSize);
            cValue = newP*meshC;
            pValue = newP*meshP;
            
            out.cValue = cValue;
            out.pValue = pValue;
            % use jackel's Lets Be Rational compiled code(mex) for price and implied vol calculation
            % blackVolLBR
            % blackPrice
            
            for i=1:strikeSize
                K = strikes(i);
                impVolP(i) = blackVolLBR(pValue(i),1.0,K, maturity/365.0,-1);
                impVolC(i) = blackVolLBR(cValue(i),1.0,K, maturity/365.0,1);
                if K <= 1.0
                     impVol(i) = impVolP(i);
                else
                     impVol(i) = impVolC(i);
                end
            end
            
            out.impVolP = impVolP;
            out.impVolC = impVolC;
            out.impVol = impVol;
            out.probMeshInt = newP;
            
        end
        
        function out = computeForwardImpVol(eqCOMDupireSpotGF,params,targetExpiry,targetStrikes)
%             expiry = params.expiry;
%             strikes = params.marketStrikes;
%             
%             %mc random number initialize
% %             NMC = 2^14;
%             NMC = params.NMC;
%             
%             MCTimeStep = length(expiry); % -1 because 0
% 
%             Ps = sobolset(MCTimeStep,'Skip',NMC);
% %             Ps = scramble(Ps,'MatousekAffineOwen');
%             Q = qrandstream(Ps);
%             
%             reset(Q);
%             U0 = qrand(Q,NMC);
%             U = zeros(NMC,MCTimeStep);
%             
%             % first random numbers goes to the enddate..
%             for i=1:size(U,2)
%                 U(:,i) = U0(:,size(U,2)-(i-1));
%             end            
%             
            targetImpVolSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            cValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            pValueSurface = zeros(length(targetExpiry),size(targetStrikes,2));
            probMeshInt = zeros(length(targetExpiry),size(targetStrikes,2));
            targetImpVolPerExpiry = zeros(1,size(targetStrikes,2));
            cValue = zeros(1,size(targetStrikes,2));
            pValue = zeros(1,size(targetStrikes,2));
            probMeshIntPerExpiry = zeros(1,size(targetStrikes,2));
            
            for i=1:length(targetExpiry)
                strikePerExpiry = targetStrikes(i,:);
                outDummy = eqCOMDupireSpotGF.computeForwardImpVolPerExpiry(targetExpiry(i),strikePerExpiry,params);
                targetImpVolPerExpiry = outDummy.impVol;
                cValue = outDummy.cValue;
                pValue = outDummy.pValue;
                probMeshIntPerExpiry = outDummy.probMeshInt;
                
                for j=1:size(targetStrikes,2)
                    targetImpVolSurface(i,j) = targetImpVolPerExpiry(j);
                    cValueSurface(i,j) = cValue(j);
                    pValueSurface(i,j) = pValue(j);
                    probMeshInt(i,j) = probMeshIntPerExpiry(j);
                end
            end
            
            out.impVolSurface = targetImpVolSurface;
            out.cValueSurface = cValueSurface;
            out.pValueSurface = pValueSurface;
            out.probMeshInt = probMeshInt;
        end
        
        %generate marginal(cumulative distribution) at each event
        %date(per expiry)
        %using conditional transition Probability matrix
        function out = generateMarginalPerExpiry(eqCOMDupireSpotGF,condProbPerExpiry,Ks)
%             Ks = params.Ks;
%             nPoints = length(params.Ks);
            
            nPoints = length(Ks);
            condProb = condProbPerExpiry;
            Qa = zeros(length(Ks),length(Ks));
            cumM = 0;
            cumM2 = 0;
            %first row dealt separately
            Qa(1,1) = condProb(1,1);
            cumM2 = 0.0;
            for j=2:nPoints
                cumM2 = cumM2 + condProb(1,j);
                Qa(1,j) = Qa(1,1) + cumM2;
            end
            
            for i=2:nPoints
                cumM = 0.0;
                Qa(i,i) = condProb(i,i);
                for j=i-1:-1:1
                    Qa(i,i) = Qa(i,i) + condProb(i,j);
                end

                cumM = 0.0;
                for j=i-1:-1:1
                    cumM = cumM + condProb(i,j+1);
                    Qa(i,j) = Qa(i,i) - cumM;
                end

                cumM2 = 0.0;
                for j=i+1:nPoints
                    cumM2 = cumM2 + condProb(i,j);
                    Qa(i,j) = Qa(i,i) + cumM2;
                end
            end
            
            out = Qa;
        end
        
        %generate marginal(cumulative distribution) for all eventdates
        %date(per expiry)
        %using conditional transition Probability matrix
        
        function marginal = generateMarginal(eqCOMDupireSpotGF,condProb,params)
            Ks = params.Ks;
            marginal = zeros(params.expirySize,length(Ks),length(Ks));
            condProbPerExpiry = zeros(length(Ks),length(Ks));
            marginalPerExpiry = zeros(length(Ks),length(Ks));
            for i=1:params.expirySize
                condProbPerExpiry(:,:) = condProb(i,:,:);
%                 marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,params);
                marginalPerExpiry = eqCOMDupireSpotGF.generateMarginalPerExpiry(condProbPerExpiry,Ks);
                marginal(i,:,:) = marginalPerExpiry(:,:);
            end
        end
        
        
        % Target function for FixedPointIteration Optimizer
        
        function  out  = TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            
            
          %% Solve  Forward PDE(GF) One time
            outGF = eqCOMDupireSpotGF.Solve1DGF(tvar,mkt_dT,optParams.dK,optParams.lastProb,optParams);
            
            newProb = outGF.newProb;
            optParams.meshProb = newProb;
           %% PDE(GF) Solve End
           % find the implied vol of dupire model
           if strcmp(eqCOMDupireSpotGF.modelParams('UseLetsBeRational'),'YES')
               target = InterpolateTargetStrikeVolFPI(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           else
               target = InterpolateTargetStrikeVolFPIBisec(eqCOMDupireSpotGF,idxNow,newProb,optParams); 
           end
           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           for i=1:optParams.strikeSize
                out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           % for shorter tenor we only fit for the restricted interval
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=1:optParams.lowerIdx-1
                    out.newLocalVol(i) = out.newLocalVol(optParams.lowerIdx);
                end

                for i=optParams.upperIdx+1:optParams.strikeSize
                    out.newLocalVol(i) = out.newLocalVol(optParams.upperIdx);
                end
            end
            
            out.volErrorTotal = 0.0;
            out.priceReTotal = 0.0;
            %for one month we only fit betwee lower and upper
            dummyN = 0;
            if idxNow <= optParams.params.numOfCutoffTenor
                for i=optParams.lowerIdx:optParams.upperIdx
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            else
                for i=1:length(out.impVolError)
                    out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
                    out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
                    dummyN = dummyN +1;
                end
            end
            out.volErrorTotal = sqrt(out.volErrorTotal/dummyN);
            out.priceReTotal = sqrt(out.priceReTotal/dummyN);
            
        end
        
         % Fixed Point Iteration Optimizer
         % start from implied vol find the local vol using Reghai's fixed
         % point iteration optimization
         % LocalVol(n+1) = LocalVol(n)*(marketImpVol)/ModelImplVol(n);
         
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqCOMDupireSpotGF,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0; % Initial ErrorBound make it big enough
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            end
            
        end
        
        % Fixed Local Vol per expiry by bootstrapping
        
        function bootStrapOut = FindVolProxy(eqCOMDupireSpotGF,idxNow,dT,lastProb,params)
            %initialize calibration parameters
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            
            optParams.meshProb = zeros(1,params.Ns);
            
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.fwdMoneyness(idxNow,i);
            end
                
%             if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
%                 % market strike points in fwd PDE grid
%                 fwdFactor = eqCOMDupireSpotGF.FwdFactor(params.expiry(idxNow));
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i)/fwdFactor;
%                 end
%             else
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i);
%                 end
%             end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastProb = lastProb;
            
            % exception for one month maturity for restricted interval
            
            lowerCutoff = params.lowerCutoffVector(idxNow);
            upperCutoff = params.upperCutoffVector(idxNow);
            numOfCutoffTenor = params.numOfCutoffTenor; 
            
            lowerIdx = 1;
            upperIdx = params.strikeSize;
            
            if idxNow <= numOfCutoffTenor
                lowerIdx = min(find(optParams.marketStrikes >= lowerCutoff));
                upperIdx = max(find(optParams.marketStrikes <= upperCutoff));
            end
            
            optParams.lowerIdx = lowerIdx;
            optParams.upperIdx = upperIdx;
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            for i=1:lowerIdx-1
                tvar(i) = tvar(lowerIdx);
            end
            
            for i=upperIdx+1:params.strikeSize
                tvar(i) = tvar(upperIdx);
            end

            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqCOMDupireSpotGF,tvar,optParams);
                
            
%             tol = 0.0001;
%             maxIter = 1000;
            
            tol = params.tol;
            maxIter = params.maxIter;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter]  = eqCOMDupireSpotGF.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            % for later use
            bootStrapOut.marketStrikes = optParams.marketStrikes;
            
            bootStrapOut.volError = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            
            bootStrapOut.nIter = nIter;
            
            out = eqCOMDupireSpotGF.Solve1DGF(bootStrapOut.volProxy,dT,optParams.dK,lastProb,optParams);
            
            bootStrapOut.lastProb = out.newProb;
            bootStrapOut.condProb = out.condProb;
            
        end
        
        function out = CalibrateToVolSurface(eqCOMDupireSpotGF,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackOTMPrices2 = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            blackOTMVega2 = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            
            dfOut = zeros(expirySize,1);
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            if strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess')
                for k=1:expirySize
    %                 fwd = black.Fwd(spot,expiry(k));
    %                 df = black.zeroCurve.DF(expiry(k)/365.0);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j);
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize

                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        if strike(j) <= 0
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        else
                            dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                            fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                        end

                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'P');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        else
                            blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                            blackOTMPrices2(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j) + 0.0001,'C');
                            blackOTMVega2(k,j) = (blackOTMPrices2(k,j) - blackOTMPrices(k,j))/0.0001;
                        end
                        blackOTMVega(k,j) = BlackFwdVega(1,fwdMoneyness(k,j),blackVol(k,j),expiry(k)/365.0);
                         
                    end
                    dfOut(k) = black.zeroCurve.DF(expiry(k)/365.0);
                end
                
            end
                
%             if strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     fwdFactor = eqCOMDupireSpotGF.FwdFactor(expiry(k));
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         fwdStrike = strike(j)/fwdFactor;
%                         if fwdStrike <= 1.0
% %                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                         else
% %                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                             blackOTMPrices(k,j)  = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMPrices2(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                             blackOTMVega(k,j) = BlackFwdVega(1,fwdStrike,blackVol(k,j),expiry(k)/365.0);
%                             
%                         end
%                     end
%                 end
%             else
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         if strike(j) <= 1
%                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                         else
%                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                         end
%                     end
%                 end
%             end
%             
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            
            params.blackVol = blackVol;
            params.fwdMoneyness = fwdMoneyness;
            
            % additional model params
            eqCOMDupireSpotGF.fwdMoneyness = fwdMoneyness;
            
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % optimizer setting
            params.tol = eqCOMDupireSpotGF.modelParams('tol');
            params.maxIter = eqCOMDupireSpotGF.modelParams('maxIter');
            
            % vol proxy calibration grid setting
            
            params.Kmin = eqCOMDupireSpotGF.modelParams('Kmin');
            params.Kmax = eqCOMDupireSpotGF.modelParams('Kmax');
            params.Ns   = eqCOMDupireSpotGF.modelParams('Ns');
            params.dK   = eqCOMDupireSpotGF.modelParams('dK');
            params.Ks   = eqCOMDupireSpotGF.modelParams('Ks');
            
            % current spot on the grid
            params.Pricingidx = floor((1.0-params.Ks(1))/params.dK) + 1;
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;      
            
            % GFType : 1 = matrix exponential moler higham
            %          2 = one step matrix exponential moler higham & multiplication from
            %          3 = one step GF & multiplication from right Andreasen & Huge
            
            params.GFType = eqCOMDupireSpotGF.modelParams('GFType');
            
            params.backGFType = eqCOMDupireSpotGF.modelParams('backGFType');
            
            params.mcOneTimeStep = eqCOMDupireSpotGF.modelParams('mcOneTimeStep');
            
            params.pricingSchemeType = eqCOMDupireSpotGF.modelParams('pricingSchemeType');
            params.NMC = eqCOMDupireSpotGF.modelParams('NMC');
            
            % backGFType : 1 = forward FD(GF)
            %              2 = implicit FD
            
            params.oneStepDt = 1.0/365.0;
            
            
            
            params.numOfCutoffTenor = eqCOMDupireSpotGF.modelParams('numOfCutoffTenor');
            
            params.lowerCutoffVector = eqCOMDupireSpotGF.modelParams('lowerCutoffVector');
            params.upperCutoffVector = eqCOMDupireSpotGF.modelParams('upperCutoffVector');
            
            
            %output vol proxy
            out.fwdMoneyness = fwdMoneyness;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.volProxyOrig = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.probMesh = zeros(params.expirySize,params.Ns);
            
            out.condProb = zeros(params.expirySize,params.Ns,params.Ns);
            
            
            %initialze the intial probability distribution in the grid
            initProb = zeros(1,params.Ns);
            initProb(params.Pricingidx) = 1.0;
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackOTMPrices2= blackOTMPrices2;
            out.blackOTMVega = blackOTMVega;
            out.blackOTMVega2 = blackOTMVega2;
            out.dfOut = dfOut;
            
            out.blackVol = blackVol;
            out.blackOTMVega = blackOTMVega;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            
            out.volError = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.marketStrikes = zeros(expirySize,strikeSize);
            
            out.Ks =  params.Ks;
            out.Pricingidx = params.Pricingidx;
            out.nIter = zeros(expirySize,1);
            out.localVol = zeros(expirySize,length(out.Ks));
            out.rmseTotal=0.0;
            out.fwdVolMseTotal = 0.0;
            
            localVolFloor = eqCOMDupireSpotGF.modelParams('localVolFloor');
            localVolCap   = eqCOMDupireSpotGF.modelParams('localVolCap');
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    
%                     tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        
                        % we apply floor and cap for the volProxy
                        
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
%                     toc
                    
%                     tic
                    % assigning the calibrated volProxy to the local vol
                    % surface
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;
                    
                    % generate marginal(cumulative) distribution for mcmc
                    % simulation
                    
                    eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.expiry = params.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = params.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
                    % calibration gives model schedule, for later use
                    % general products such as autocallables..
                    
                    eqCOMDupireSpotGF.modelSchedule = eqCOMDupireSpotGF.localVolSurface.expiry;
                    
                    params.marketStrikes = out.marketStrikes;
                    
%                     toc
                    
%                     calculate backward scheme for given target
%                     compareforwardMCFlag = 1 for one step euler scheme
%                     compareforwardMCFlag = 2 for daily euler scheme
%                     
%                     compareforwardMCFlag = 3 for markov chain monte carlo
                     
                    
                    pricingSchemeType = params.pricingSchemeType; 
                    
%                     tic
                    
                    if pricingSchemeType == 1
                        out.pdeOTMPrices = eqCOMDupireSpotGF.computeBackwardPDEOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backReOrig = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backPriceOrigRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.pdeOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                out.backReOrig(i,j) = out.pdeOTMPrices(i,j)/out.blackOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.pdeOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backPriceOrigRmseTotal = out.backPriceOrigRmseTotal + out.backReOrig(j,k)*out.backReOrig(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backPriceOrigRmseTotal= sqrt(out.backPriceOrigRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
  
                    elseif pricingSchemeType == 3
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCOTMTotal(params);

                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                    
                    elseif pricingSchemeType == 4
                        out.mcOTMPrices = eqCOMDupireSpotGF.computeForwardMCMCOTMTotal(params);
                        out.backRe = zeros(expirySize,strikeSize);
                        out.backwardVol = zeros(expirySize,strikeSize);
                        out.backVolError = zeros(expirySize,strikeSize);

                        out.backPriceRmseTotal = 0.0;
                        out.backVolMseTotal = 0.0;
                        for i=1:expirySize
                            for j=1:strikeSize
                                out.backRe(i,j) = out.mcOTMPrices(i,j)/out.dupireOTMPrices(i,j)-1;
                                if out.marketStrikes(i,j) <=1.0
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,-1);
                                else
                                    out.backwardVol(i,j) = blackVolLBR(out.mcOTMPrices(i,j),1,out.marketStrikes(i,j),params.expiry(i)/365.0,1);
                                end
                                out.backVolError(i,j) = out.backwardVol(i,j) - out.marketImpVol(i,j);

                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                out.backPriceRmseTotal = out.backPriceRmseTotal + out.backRe(j,k)*out.backRe(j,k);
                                out.backVolMseTotal = out.backVolMseTotal +out.backVolError(j,k)*out.backVolError(j,k);
                                N=N+1;
                            end
                        end

                        out.backPriceRmseTotal = sqrt(out.backPriceRmseTotal/N);
                        out.backVolMseTotal=sqrt(out.backVolMseTotal/N);
                        
                    end

%                     toc
                case 'bootstrapForward'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    % compute implied surface for targetStrikes;
                    targetExpiry = params.expiry;
                    
                    %% at T call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVol = outDummy.impVolSurface;
                    out.cValueSurface = outDummy.cValueSurface;
                    out.pValueSurface = outDummy.pValueSurface;
                    out.probMeshInt = outDummy.probMeshInt;
                    
                     %% at T-dT call & put price
                    for idx1=1:length(params.expiry)
                        targetExpiry(idx1) = params.expiry(idx1)-0.000001;
%                         targetExpiry(idx1) = params.expiry(idx1)+1;
                    end
                    
%                     targetStrikes = out.marketStrikes;
                    % 0.5% shifted grid
                    newKs = zeros(length(out.Ks),1);
                    newKs = zeros(241,1);
                    
                    for idx1=1:241
                        newKs(idx1) = 0.1+ 0.01*(idx1-1);
                    end
                    
                    targetStrikes = zeros(length(targetExpiry),length(newKs));
                    for idx1=1:size(out.marketStrikes,1)
                        for idx2= 1:length(newKs)
%                             targetStrikes(idx1,idx2) = out.Ks(idx2);
                            targetStrikes(idx1,idx2) = newKs(idx2);
                        end
                    end
                    
                    outDummy = eqCOMDupireSpotGF.computeForwardImpVol(params,targetExpiry,targetStrikes);
                    out.forwardImpVolPrev = outDummy.impVolSurface;
                    out.cValueSurfacePrev = outDummy.cValueSurface;
                    out.pValueSurfacePrev = outDummy.pValueSurface;
                    out.probMeshIntPrev = outDummy.probMeshInt;
                    
                    aaa = 1.0;
                    
                case 'bootstrapForwardOnly'
                    
                    tic
                    %vol proxy calibration
                    lastProb = initProb;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqCOMDupireSpotGF.FindVolProxy(i,dT,lastProb,params);
                        for j=1:strikeSize
                            out.volProxyOrig(i,j) = bootStrapOut.volProxy(j);
                            out.volProxy(i,j) = min(max(bootStrapOut.volProxy(j),localVolFloor),localVolCap);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.volError(i,j) = bootStrapOut.volError(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                            out.marketStrikes(i,j) = bootStrapOut.marketStrikes(j);
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqCOMDupireSpotGF.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos,i);
                        for j=1:params.Ns
                            out.probMesh(i,j) = bootStrapOut.lastProb(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        
                        out.condProb(i,:,:) = bootStrapOut.condProb;
                        % Initial Payoff for the next period
                        lastProb = bootStrapOut.lastProb;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.priceReOrig(j,k)*out.priceReOrig(j,k);
                            out.fwdVolMseTotal = out.fwdVolMseTotal + out.volError(j,k)*out.volError(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    out.fwdVolMseTotal = sqrt(out.fwdVolMseTotal/N);
                    toc
                    
                    % update calibration result for eqComDupire
                    
                    eqCOMDupireSpotGF.localVolSurface.volProxy = out.volProxy;
                    eqCOMDupireSpotGF.localVolSurface.ipos = out.ipos;
                    eqCOMDupireSpotGF.localVolSurface.localVol = out.localVol;
                    eqCOMDupireSpotGF.localVolSurface.probMesh = out.probMesh;
                    eqCOMDupireSpotGF.localVolSurface.condProb = out.condProb;

                    eqCOMDupireSpotGF.localVolSurface.Ks = out.Ks;
                    eqCOMDupireSpotGF.localVolSurface.Pricingidx = out.Pricingidx;
                    eqCOMDupireSpotGF.localVolSurface.expiry = out.expiry;
                    eqCOMDupireSpotGF.localVolSurface.strike = out.strike;
                    eqCOMDupireSpotGF.localVolSurface.marketStrikes = out.marketStrikes;
                    
%                     eqCOMDupireSpotGF.localVolSurface.marginal = eqCOMDupireSpotGF.generateMarginal(out.condProb,params);
                    
                    aaa = 1.0;
                    
                    
                      

                otherwise
                    disp('unImplemented')
                    
            end
        end
             
    end
    
end



In [ ]:
classdef EQCOMDupireSpot < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        % vol functor
        localVolSurface
        modelSchedule
    end
    
    methods
        function eqDupireSpot = EQCOMDupireSpot(EQModel)
            if nargin > 0
                eqDupireSpot.zeroCurve = EQModel.zeroCurve;
                eqDupireSpot.dividendCurve = EQModel.dividendCurve;
                eqDupireSpot.repoRateCurve = EQModel.repoRateCurve;
                eqDupireSpot.forwardCurve = EQModel.forwardCurve;
                
                eqDupireSpot.spot = EQModel.spot;
                eqDupireSpot.mktData =  EQModel.mktData;
                eqDupireSpot.modelParams = EQModel.modelParams;
                eqDupireSpotGF.modelSchedule = [];
            end
        end
        
        function path= bbgenerator(eqDupireSpot,rn)
            %generate brownian bridge motion,please refer to peter jackel's book for
            %detail;
            %
            %Date:2006-8-29

            [Npaths,Nsteps]=size(rn);
            path=zeros(Npaths,Nsteps);
            map= zeros(1,Nsteps);
            bridgeindex = zeros(1,Nsteps);
            leftindex = zeros(1,Nsteps);
            rightindex = zeros(1,Nsteps);
            sigma = zeros(1,Nsteps);
            leftweight = zeros(1,Nsteps);
            rightweight = zeros(1,Nsteps);
            
            map(Nsteps)=1;
            bridgeindex(1)=Nsteps;
            sigma(1)=sqrt(Nsteps);
            leftweight(1)=1; %////////////////
            rightweight(1)=1; %////////////////
            j=1;
            for i=2:Nsteps    
                while map(j) %////////////////////
                    j=j+1;
                end
                k=j;
                while ~map(k) % //////////////
                    k=k+1;
                end
                l=j+fix((k-1-j)/2);
                map(l)=i;
                bridgeindex(i)=l;
                leftindex(i)=j;
                rightindex(i)=k;
                leftweight(i)  = (k-l)/(k+1-j);
                rightweight(i) = (l+1-j)/(k+1-j);
                sigma(i) = sqrt(((l+1-j)*(k-l))/(k+1-j));
                j=k+1;
                if j>=Nsteps+1
                    j=1;
                end
            end

            path(:,Nsteps)=sigma(1)*rn(:,1);
            for i=2:Nsteps
                j=leftindex(i);
                k=rightindex(i);
                l=bridgeindex(i);
                if j~=1
                    path(:,l)=leftweight(i)*path(:,j-1) + rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                else
                    path(:,l) = rightweight(i)*path(:,k) + sigma(i)*rn(:,i);
                end
            end
        end
        
        function out = TDMASolve(eqDupireSpot,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqDupireSpot,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function localVol = GetLocalVolFromProxy(eqDupireSpot,volProxy,Ks,ipos)
            localVol = zeros(length(Ks),1);
            
            for i=1: length(volProxy)
%                 Extrapolation at the left and right
                if i == 1
                    for j=1:ipos(i)-1
                        localVol(j) = volProxy(i);
                    end
                elseif i == length(volProxy)
                    for j=ipos(i-1):ipos(i)-1
                        localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                    end
                    for j=ipos(i):length(Ks)
                        localVol(j) = volProxy(i);
                    end
%                  linear interpolation in the spot grid in-between    
                else
                    for j=ipos(i-1):ipos(i)-1
                        localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                    end
                end
            end
            
        end
        
        function [newC newP] = Solve1DPDE(eqDupireSpot,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            proxy = eqDupireSpot.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos);
            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);

            dK2 = dK*dK;
            for i=2:tdma.size-1
                tdma.a(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.b(i) = 1 + dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
                tdma.c(i) = -0.5*dT*proxy(i)*proxy(i)*optParams.Ks(i)*optParams.Ks(i)/dK2;
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqDupireSpot.LUDecompose(tdma);
            pmeshC = eqDupireSpot.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqDupireSpot.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = InterpolateTargetStrikeVolFPI(eqDupireSpot,idxNow,meshC,meshP,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            strikes = params.marketStrikes;
            strikeSize = length(params.marketStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            out.interpBlackPrices = zeros(strikeSize,1);
            for i=1:strikeSize
                K = strikes(i);
                %linear interpolated option values
                NGP = floor((K-params.Ks(1))/params.params.dK);
                % corrected distance index
                NGP = NGP +1;
                if NGP < 1
                    NGP = 1;
                elseif NGP >= params.params.Ns
                    NGP = params.params.Ns-1;
                end

                alpha = (K-params.params.Ks(NGP))/params.dK;
                cValue = (1-alpha)*meshC(NGP) + alpha*meshC(NGP+1);
                pValue = (1-alpha)*meshP(NGP) + alpha*meshP(NGP+1);
                if K <= 1.0
%                      out.vols(i) = BisecBlackFwdIV('P',1.0,K, ...
%                                       0.0,params.params.expiry(idxNow)/365.0,a,b,pValue,Tol,MaxIter);
                     
                     out.vols(i) = blackVolLBR(pValue,1.0,K, params.params.expiry(idxNow)/365.0,-1);
                     out.interpOTMPrices(i) = pValue;
%                      out.interpBlackPrices(i) = BlackFwdPrice('P',1.0,K,0.0,out.vols(i),params.params.expiry(idxNow)/365.0);
                     out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,-1);
                else
%                     out.vols(i) = BisecBlackFwdIV('C',1.0,K, ...
%                                       0.0,params.params.expiry(idxNow)/365.0,a,b,cValue,Tol,MaxIter);
                    
                    out.vols(i) = blackVolLBR(cValue,1.0,K, params.params.expiry(idxNow)/365.0,1);
                    out.interpOTMPrices(i) = cValue;
%                     out.interpBlackPrices(i) =
%                     BlackFwdPrice('C',1.0,K,0.0,out.vols(i),params.params.expiry(idxNow)/365.0);
                    out.interpBlackPrices(i) = blackPrice(1.0,K,out.vols(i),params.params.expiry(idxNow)/365.0,1);
                end
            end
            
            
        end
        
        function out = CalculateTarget(eqDupireSpot,idxNow,meshC,meshP,optParams)
            % Calculate Object Function
            
            out.dupireOTMPrice = zeros(optParams.strikeSize,1);
            out.re = zeros(optParams.strikeSize,1);
            
            for i=1:optParams.strikeSize
                K = optParams.marketStrikes(i);
                %linear interpolated option values
                NGP = floor((K-optParams.Ks(1))/optParams.dK);
                % corrected distance index
                NGP = NGP +1;
                if NGP < 1
                    NGP = 1;
                elseif NGP >= optParams.meshSize
                    NGP = optParams.meshSize-1;
                end

                alpha = (K-optParams.Ks(NGP))/optParams.dK;
                cValue = (1-alpha)*meshC(NGP) + alpha*meshC(NGP+1);
                pValue = (1-alpha)*meshP(NGP) + alpha*meshP(NGP+1);
                if K <= 1
                    out.re(i) = pValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                    out.dupireOTMPrice(i) = pValue;
                else
                    out.re(i) = cValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                    out.dupireOTMPrice(i) = cValue;
                end
            end
            
            
        end
        
        function  out  = TargetFunctionVolProxyLevMar(eqDupireSpot,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            %filling vol proxy grid with the tvar
          %% Solve  Forward PDE One time
            [newC newP] = eqDupireSpot.Solve1DPDE(tvar,mkt_dT,optParams.dK,optParams.lastC,optParams.lastP,optParams);
            optParams.meshC = newC;
            optParams.meshP = newP;
           %% PDE Solve End
            target = CalculateTarget(eqDupireSpot,idxNow,newC,newP,optParams);
            out = target.re;
        end
        
        function  out  = TargetFunctionVolProxy(eqDupireSpot,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            %filling vol proxy grid with the tvar
          %% Solve  Forward PDE One time
            [newC newP] = eqDupireSpot.Solve1DPDE(tvar,mkt_dT,optParams.dK,optParams.lastC,optParams.lastP,optParams);
            optParams.meshC = newC;
            optParams.meshP = newP;
           %% PDE Solve End
            target = CalculateTarget(eqDupireSpot,idxNow,newC,newP,optParams);
            out = 0.0;
            for i=1:length(target.re)
                out = out + target.re(i)*target.re(i);
            end
        end
        
        function  out  = TargetFunctionVolProxyFPI(eqDupireSpot,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            %filling vol proxy grid with the tvar
          %% Solve  Forward PDE One time
            [newC newP] = eqDupireSpot.Solve1DPDE(tvar,mkt_dT,optParams.dK,optParams.lastC,optParams.lastP,optParams);
            optParams.meshC = newC;
            optParams.meshP = newP;
           %% PDE Solve End
           % find the implied vol of dupire model
           target = InterpolateTargetStrikeVolFPI(eqDupireSpot,idxNow,newC,newP,optParams); 

           marketImpVol = optParams.params.blackVol;
           expiry = optParams.params.expiry;
           strike = optParams.params.strike;
           
           out.newLocalVol = zeros(length(optParams.strikeSize),1);
           out.localVolError = zeros(length(optParams.strikeSize),1);
           out.impVolError =  zeros(length(optParams.strikeSize),1);
           out.modelImpVol = zeros(length(optParams.strikeSize),1);
           out.marketImpVol = zeros(length(optParams.strikeSize),1);
           out.interpOTMPrices = zeros(length(optParams.strikeSize),1);
           out.interpBlackPrices = zeros(length(optParams.strikeSize),1);
           out.priceRe = zeros(length(optParams.strikeSize),1);
           
           % fixed point iteration update rule:: targetType : 1 = localVol(n+1) = localVol(n)*ImpVol(market)/ImpVol(model,localVol(n))
           %                                                 2 = localVol(n+1) = localVol(n)*Price(market)/Price(model,localVol(n))
                                                      
           if optParams.params.localVolIterType == 1
               for i=1:optParams.strikeSize
                    out.newLocalVol(i) = tvar(i)*(marketImpVol(idxNow,i))/target.vols(i);
               end
           else
               for i=1:optParams.strikeSize
                    out.newLocalVol(i) = tvar(i)*(optParams.params.blackOTMPrices(idxNow,i))/target.interpOTMPrices(i);
               end
           end
           
           
           for i=1:optParams.strikeSize
                out.localVolError(i) = out.newLocalVol(i) - tvar(i);
                out.modelImpVol(i) = target.vols(i);
                out.marketImpVol(i) =  marketImpVol(idxNow,i);
                out.impVolError(i) = out.modelImpVol(i) - out.marketImpVol(i);
                out.interpOTMPrices(i) = target.interpOTMPrices(i);
                out.interpBlackPrices(i) = target.interpBlackPrices(i);
                out.priceRe(i) = out.interpOTMPrices(i)/optParams.params.blackOTMPrices(idxNow,i)-1.0;
           end
           
           
            out.volErrorTotal = 0.0;
            for i=1:length(out.impVolError)
                out.volErrorTotal = out.volErrorTotal + out.impVolError(i)*out.impVolError(i);
            end
            
            out.volErrorTotal = sqrt(out.volErrorTotal/length(out.impVolError));
            out.priceReTotal = 0.0;
            for i=1:length(out.priceRe)
                out.priceReTotal = out.priceReTotal + out.priceRe(i)*out.priceRe(i);
            end
            out.priceReTotal = sqrt(out.priceReTotal/length(out.priceRe));
            
        end
        
        function [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = FixedPointIter(eqDupireSpot,targetfunc,tvar,tol,maxIter,optParams)
            
            n= 0;
            errorTry = 1000.0;
            tvarOld = tvar;
            if optParams.params.targetType == 1
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce implied vol error
                    errorTry = out.volErrorTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
            else
                while (errorTry > tol) && (n < maxIter)
                    out = targetfunc(tvar);
                    tvarOld = tvar;
                    % reduce price relative error
                    errorTry = out.priceReTotal;
                    tvar = out.newLocalVol;
                    n = n+1;
                end
                x = tvar;
                finalOut = targetfunc(tvarOld);
                fval = finalOut.volErrorTotal;
                marketImpVol = finalOut.marketImpVol;
                modelImpVol  = finalOut.modelImpVol;
                interpBlackPrices = finalOut.interpBlackPrices;
                interpOTMPrices = finalOut.interpOTMPrices;
                volError     = finalOut.impVolError;
                volErrorTotal = finalOut.volErrorTotal;
                priceRe      = finalOut.priceRe;
                priceReTotal = finalOut.priceReTotal;
                nIter = n;
                
            end
        end
        
        function bootStrapOut = FindVolProxy(eqDupireSpot,idxNow,dT,lastC,lastP,params)
            %initialize calibration parameters
            
            for i=1:params.strikeSize
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            optParams.meshC = zeros(params.Ns,1);
            optParams.meshP = zeros(params.Ns,1);
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrices = params.blackOTMPrices;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
%             if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
%                 % market strike points in fwd PDE grid
%                 fwdFactor = eqDupireSpot.FwdFactor(params.expiry(idxNow));
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i)/fwdFactor;
%                 end
%             else
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = params.strike(i);
%                 end
%             end
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = params.fwdMoneyness(idxNow,i);
            end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;  % add default 1
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastC = lastC;
            optParams.lastP = lastP;
            
            targetfunc = @(tvar) TargetFunctionVolProxyFPI(eqDupireSpot,tvar,optParams);
            tol = 0.0001;
            maxIter = 1000;
            
            [x, fval,marketImpVol,modelImpVol,interpBlackPrices, interpOTMPrices,volError,volErrorTotal, priceRe, priceReTotal,nIter] = eqDupireSpot.FixedPointIter(targetfunc,tvar,tol,maxIter,optParams);
            
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = x(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            bootStrapOut.re = volError;
            bootStrapOut.marketImpVol = marketImpVol;
            bootStrapOut.modelImpVol = modelImpVol;
            bootStrapOut.interpBlackPrices = interpBlackPrices;
            bootStrapOut.dupireOTMPrices = interpOTMPrices;
            bootStrapOut.priceRe = priceRe;
            bootStrapOut.nIter = nIter;
            
            
            [newC newP] = eqDupireSpot.Solve1DPDE(bootStrapOut.volProxy,dT,optParams.dK,lastC,lastP,optParams);
            bootStrapOut.lastC = newC;
            bootStrapOut.lastP = newP;
        end
        
        function out = CalibrateToVolSurface(eqDupireSpot,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrices = zeros(expirySize,strikeSize);
            blackVol = zeros(expirySize,strikeSize);
            
            % we add blackvol as matrix so that in the calibation we don't
            % need to do 2D interpolation again and again!!
            % also for the target black price too!!
            
            for k=1:expirySize
%                 fwd = black.Fwd(spot,expiry(k));
%                 df = black.zeroCurve.DF(expiry(k)/365.0);
                for j=1:strikeSize
                    blackVol(k,j) = volSurface.volSurfaceR(k,j);
                    if strike(j) <= 0
                        dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                        fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                    else
                        dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                        fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
                    end
                    
                    if fwdMoneyness(k,j) <= 1
                        blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                    else
                        blackOTMPrices(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                    end
                end
            end
                
%             if strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     fwdFactor = eqDupireSpot.FwdFactor(expiry(k));
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         fwdStrike = strike(j)/fwdFactor;
%                         if fwdStrike <= 1.0
% %                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,-1);
%                         else
% %                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,spot*strike(j)/fwd,blackVol(k,j),expiry(k)/365.0,1);
%                         end
%                     end
%                 end
%             else
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     for j=1:strikeSize
%                         blackVol(k,j) = volSurface.vol(expiry(k),strike(j));
%                         if strike(j) <= 1
% %                             blackOTMPrices(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,strike(j),blackVol(k,j),expiry(k)/365.0,-1);
%                         else
%                             blackOTMPrices(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                             blackOTMPrices(k,j) = blackPrice(1.0,strike(j),blackVol(k,j),expiry(k)/365.0,1);
%                         end
%                     end
%                 end
%             end
            
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            
            params.blackOTMPrices = blackOTMPrices;
            params.blackVol = blackVol;
            params.fwdMoneyness = fwdMoneyness;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % vol proxy calibration grid setting
            params.Kmin = 0.1;
            params.Kmax = 2.5;
            params.Ns = 241;
            params.Nt = 1;
            params.dK = (params.Kmax - params.Kmin)/(params.Ns-1);
            for i=1:params.Ns
                params.Ks(i) = params.Kmin + params.dK*(i-1);
            end
            
            % targetType : 1 = implied vol diff
            %              2 = price relative error  
            params.targetType = 1;
            
            % fixed point iteration update rule:: targetType : 1 =  localVol(n+1) = localVol(n)*ImpVol(market)/ImpVol(model,localVol(n))
            %                                                  2 =  localVol(n+1) = localVol(n)*Price(market)/Price(model,localVol(n))  
            
            params.localVolIterType = 1;
            
            
            %output vol proxy
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.callMesh = zeros(params.expirySize,params.Ns);
            out.putMesh = zeros(params.expirySize,params.Ns);
            % output localvol setting
            out.dK = params.dK;
            out.localVolSurface.strikeSize = params.Ns;
            out.Ks = zeros(params.Ns,1);
            for i=1:params.Ns
                out.Ks(i) = params.Kmin + out.dK*(i-1);
            end
            
            %initialze the intial call & put payoff in fwd PDE grid
            initC = zeros(params.Ns,1);
            initP = zeros(params.Ns,1);
            for i=1:params.Ns
                initC(i) = max(1-out.Ks(i),0.0);
                initP(i) = max(out.Ks(i)-1,0.0);
            end
            
            out.blackOTMPrices = blackOTMPrices;
            out.blackVol = blackVol;
            
            out.marketImpVol = zeros(expirySize,strikeSize);
            out.modelImpVol  = zeros(expirySize,strikeSize);
            
            out.interpBlackPrices = zeros(expirySize,strikeSize);
            out.dupireOTMPrices = zeros(expirySize,strikeSize);
            
            out.dupireBlackVol = zeros(expirySize,strikeSize);
            out.re = zeros(expirySize,strikeSize);
            out.priceRe = zeros(expirySize,strikeSize);
            out.priceReOrig = zeros(expirySize,strikeSize);
            
            out.nIter = zeros(expirySize,1);
            
            out.Ks = params.Ks;
            out.localVol = zeros(expirySize,length(out.Ks)); 
            out.rmseTotal=0.0;
            
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    %vol proxy calibration
                    lastC = initC;
                    lastP = initP;
                    
            
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqDupireSpot.FindVolProxy(i,dT,lastC,lastP,params);
                        for j=1:strikeSize
                            out.volProxy(i,j) = bootStrapOut.volProxy(j);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.re(i,j) = bootStrapOut.re(j);
                            out.marketImpVol(i,j) =  bootStrapOut.marketImpVol(j);
                            out.modelImpVol(i,j) =  bootStrapOut.modelImpVol(j);
                            out.interpBlackPrices(i,j) = bootStrapOut.interpBlackPrices(j);
                            out.dupireOTMPrices(i,j) = bootStrapOut.dupireOTMPrices(j);
                            out.priceRe(i,j) = out.dupireOTMPrices(i,j)/out.interpBlackPrices(i,j)-1.0;
                            out.priceReOrig(i,j) = out.dupireOTMPrices(i,j)/out.blackOTMPrices(i,j)-1.0;
                        end
                        
                        out.nIter(i) = bootStrapOut.nIter;
                        tempLocalVol = eqDupireSpot.GetLocalVolFromProxy(bootStrapOut.volProxy,out.Ks,bootStrapOut.ipos);
                        
                        for j=1:params.Ns
                            out.callMesh(i,j) = bootStrapOut.lastC(j);
                            out.putMesh(i,j) = bootStrapOut.lastP(j);
                            out.localVol(i,j) = tempLocalVol(j);
                        end
                        % Initial Payoff for the next period
                        lastC = bootStrapOut.lastC;
                        lastP = bootStrapOut.lastP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    
                    eqDupireSpot.localVolSurface.volProxy = out.volProxy;
                    eqDupireSpot.localVolSurface.ipos = out.ipos;
                    eqDupireSpot.localVolSurface.localVol = out.localVol;
%                     eqDupireSpot.localVolSurface.probMesh = out.probMesh;
                    eqDupireSpot.localVolSurface.Ks = out.Ks;
                    eqDupireSpot.localVolSurface.expiry = params.expiry;
                    eqDupireSpot.localVolSurface.strike = params.strike;
                    
 
                    
                otherwise
                    disp('unImplemented')
            end
        end 
             
    end
    
end



In [ ]:
classdef EQCOMDupireHeston < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        % vol functor
        impliedVolSurface
        localVolSurface
        fwdMoneyNess
        numOfFactors
        
        slope
        
        % heston model related
        kappa
        theta
        rho
        sigma
        v0
        
        
        quadrature_NumOfWeights
        quadrature_nodesAndWeights
        maxIter
        calibrationErrorType
        modelPriceFormula
        strikeUseBound
        
        %fixedStrike    
        settleFutures
        settleFuturesRef
        atmVols
        
        deltaH
        useYN
        deltaCutOff
        
       %reducedFutures
        reducedFutures
    end
    
    methods
        function eqHeston = EQCOMDupireHeston(EQModel)
            if nargin > 0
                eqHeston.zeroCurve = EQModel.zeroCurve;
                eqHeston.dividendCurve = EQModel.dividendCurve;
                eqHeston.repoRateCurve = EQModel.repoRateCurve;
                eqHeston.forwardCurve = EQModel.forwardCurve;
              %% SSR
                eqHeston.referenceForwardCurve = EQModel.referenceForwardCurve;
                
                eqHeston.spot = EQModel.spot;
                eqHeston.mktData =  EQModel.mktData;
                eqHeston.modelParams = EQModel.modelParams;
                
              %% SSR modelparams start
                
                if isKey(EQModel.modelParams,'slope')
                    eqHeston.slope = EQModel.modelParams('slope');
                else
                    eqHeston.slope = 0.0;
                end
                
              %% SSR modelparams end
              
                eqHeston.kappa = EQModel.modelParams('kappa');
                eqHeston.theta = EQModel.modelParams('theta');
                eqHeston.rho   = EQModel.modelParams('rho');
                
                eqHeston.sigma = EQModel.modelParams('sigma');
                eqHeston.v0    = EQModel.modelParams('v0');
                
                % 2 factor heston vol model
                eqHeston.numOfFactors = 2;
                
                if strcmp(eqHeston.modelParams('quadrature_generateNodesYN'),'false')
                    eqHeston.quadrature_nodesAndWeights = eqHeston.modelParams('quadrature_nodesAndWeights');
                    eqHeston.quadrature_NumOfWeights = size(eqHeston.quadrature_nodesAndWeights,1);
                else
                    % quadrature setting
                    if isKey(eqHeston.modelParams,'quadrature_NumOfWeights')
                        eqHeston.quadrature_NumOfWeights = EQModel.modelParams('quadrature_NumOfWeights');
                    else
                        eqHeston.quadrature_NumOfWeights = 32;
                    end
                    
                    eqHeston.quadrature_nodesAndWeights = eqHeston.GenerateGaussLaguerre(eqHeston.quadrature_NumOfWeights);
                    
                end
                
                
                % quadrature setting
                if isKey(eqHeston.modelParams,'maxIter')
                    eqHeston.maxIter = EQModel.modelParams('maxIter');
                else
                    eqHeston.maxIter = 1000;
                end
                
                if isKey(eqHeston.modelParams,'calibrationErrorType')
                    eqHeston.calibrationErrorType = EQModel.modelParams('calibrationErrorType');
                else
                    eqHeston.calibrationErrorType = 'impVolError';
                end
                
                if isKey(eqHeston.modelParams,'modelPriceFormula')
                    eqHeston.modelPriceFormula = EQModel.modelParams('modelPriceFormula');
                else
                    eqHeston.modelPriceFormula = 'Rouah';
                end
                
                if isKey(eqHeston.modelParams,'strikeUseBound')
                    eqHeston.strikeUseBound = EQModel.modelParams('strikeUseBound');
                else
                    strikeUseBound = [30	0.8	1.2
                                    91	0.8	1.2
                                    182	0.7	1.3
                                    365	0.5	1.5
                                    730	0.5	1.5
                                    1095	0.5	1.5
                                    1460	0.5	1.5
                                    1825	0.5	1.5
                                    ];
                    eqHeston.strikeUseBound = strikeUseBound;
                end
                
                eqHeston.impliedVolSurface = eqHeston.mktData('impliedVolSurface');
                eqHeston.localVolSurface = EQModel.modelParams('localVolSurface');
                eqHeston.fwdMoneyNess = [];
                
                if ~isKey(EQModel.modelParams,'settleFutures')
                    eqHeston.settleFutures= [];
                else
                    eqHeston.settleFutures= EQModel.modelParams('settleFutures');
                end
                
                if ~isKey(EQModel.modelParams,'settleFuturesRef')
                    eqHeston.settleFuturesRef= [];
                else
                    eqHeston.settleFuturesRef = EQModel.modelParams('settleFuturesRef');
                end
                
                if ~isKey(EQModel.modelParams,'atmVols')
                    eqHeston.atmVols= [];
                else
                    eqHeston.atmVols = EQModel.modelParams('atmVols');
                end
                
                
                
                
            end
        end
        
        function out = GenerateGaussLaguerre(eqHeston,n)
            % Generate abscissas (x) and weights (w) for Gauss Laguerre integration

            % The Laguerre polynomial
            for k=0:n
                L(k+1) = (-1)^k/factorial(k)*nchoosek(n,k);
            end

            % Need to flip the vector to get the roots in the correct order
            L = fliplr(L);

            % Find the roots.  
            x = flipud(roots(L));

            % Find the weights
            w = zeros(n,1);
            for j=1:n
                % The coefficients of the derivative of the Laguerre polynomial
                for k=1:n
                    dL(k,j) = (-1)^k/factorial(k-1)*nchoosek(n,k)*x(j)^(k-1);
                end
                % The weight w(j)
                w(j) = 1/x(j)/sum(dL(:,j))^2;
                % The total weight w(j)exp(x(j))
                w(j) = w(j)*exp(x(j));
            end
            
            out = zeros(n,2);
            for j=1:n
                out(j,1) = x(j);
                out(j,2) = w(j);
            end
            
        end
        
        function out = HestonProb(eqHeston,phi,kappa,theta,rho,sigma,term,spotPrice,strikePrice,...
                                                     impliedRepoRate,v0,pNum,cpxLog)
            
            x  = log(spotPrice);
            sx = log(strikePrice);
            dd = x + impliedRepoRate*term;
            sigma2 = sigma * sigma;
            rsigma = rho * sigma;
             
            if (pNum == 1) 
                t0 = kappa - rho * sigma;
            else
                t0 = kappa;
            end
            
            rpsig = rsigma * phi;
            
            t1 = t0 + complex(0.0,-rpsig);
            if pNum == 1
                d = sqrt(t1*t1 - sigma2*phi*complex(-phi,1));
            else
                d = sqrt(t1*t1 - sigma2*phi*complex(-phi,-1));
            end
            
            ex = exp(-d*term);
            
            if strcmp(cpxLog,'Gatheral')
                if abs(phi) > 1e-8
                    if sigma > 1e-5
                        p = (t1-d)/(t1+d);
                        g = log((1.0-p*ex)/(1.0-p));
                        
                        D = v0*(t1-d)*(1.0-ex)/(sigma2*(1.0-ex*p));
                        C = kappa*theta/sigma2*((t1-d)*term -2.0*g);
                        out = imag(exp(D+C+complex(0.0,phi*(dd - sx))))/phi;
                    else
                         if pNum == 1
                             td = phi/(2.0*t1)*complex(-phi,1);
                         else
                             td = phi/(2.0*t1)*complex(-phi,-1);
                         end
                         
                         p = td*sigma2/(t1+d);
                         g = p*(1.0 -ex);
                         
                         D = v0*td*(1.0-ex)/(1.0-p*ex);
                         C = kappa*theta*(td*term - 2.0*g/sigma2);
                         out = imag(exp(D+C+complex(0.0,phi*(dd - sx))))/phi;
                    end
                else
                    error('not implemented for phi == 0 case !')
                end
            else
                error('notImplemented!')
            end
        end
        
        function out = HestonPriceGaussLaguerre(eqHeston,spotPrice,strikePrice,termDay,optionType)
            
%             spotPrice = params('spotPrice');
%             strikePrice = params('strikePrice');
%             termDay = params('termDay');
            term = termDay/365.0;
            
            fwd = eqHeston.Fwd(spotPrice,termDay);
            
            impliedRepoRate = log(fwd/spotPrice)/term;
            
            kappa = eqHeston.kappa;
            theta = eqHeston.theta;
            rho   = eqHeston.rho;
            
            sigma = eqHeston.sigma;
            v0    = eqHeston.v0;
            
            x = eqHeston.quadrature_nodesAndWeights(:,1);
            w = eqHeston.quadrature_nodesAndWeights(:,2);
            
            int1 = zeros(length(x),1);
            int2 = zeros(length(x),1);
            
%             for k=length(x):-1:1
                
            for k=1:length(x)                                    
                int1(k) = w(k) * eqHeston.HestonProb(x(k),kappa,theta,eqHeston.rho,sigma,term,spotPrice,strikePrice,...
                                                    impliedRepoRate,v0,1,'Gatheral');
                int2(k) = w(k) * eqHeston.HestonProb(x(k),kappa,theta,rho,sigma,term,spotPrice,strikePrice,...
                                                    impliedRepoRate,v0,2,'Gatheral');
            end
            
            p1 = 1/pi*sum(int1);
            
            p2 = 1/pi*sum(int2);
            
%             optionType = params('optionType');
            
            switch  optionType
                case 'Call'
                    out = fwd*(p1 + 0.5) - strikePrice*(p2 + 0.5);
                case 'Put'
                    out = fwd*(p1 - 0.5) - strikePrice*(p2 - 0.5);
                otherwise
                    error('not supported! only Call or Put')
            end
                
            
        end
        
        function out = HestonPriceGaussLaguerreFwdMon(eqHeston,spotPrice,strikePrice,termDay,optionType)
            
%             spotPrice = params('spotPrice');
%             strikePrice = params('strikePrice');
%             termDay = params('termDay');
            term = termDay/365.0;
            
%             fwd = eqHeston.Fwd(spotPrice,termDay);
            fwd = 1.0;
            
%             impliedRepoRate = log(fwd/spotPrice)/term;
            impliedRepoRate = 0.0;
            
            kappa = eqHeston.kappa;
            theta = eqHeston.theta;
            rho   = eqHeston.rho;
            
            sigma = eqHeston.sigma;
            v0    = eqHeston.v0;
            
            x = eqHeston.quadrature_nodesAndWeights(:,1);
            w = eqHeston.quadrature_nodesAndWeights(:,2);
            
            int1 = zeros(length(x),1);
            int2 = zeros(length(x),1);
            
%             for k=length(x):-1:1
                
            for k=1:length(x)                                    
                int1(k) = w(k) * eqHeston.HestonProb(x(k),kappa,theta,eqHeston.rho,sigma,term,spotPrice,strikePrice,...
                                                    impliedRepoRate,v0,1,'Gatheral');
                int2(k) = w(k) * eqHeston.HestonProb(x(k),kappa,theta,rho,sigma,term,spotPrice,strikePrice,...
                                                    impliedRepoRate,v0,2,'Gatheral');
            end
            
            p1 = 1/pi*sum(int1);
            
            p2 = 1/pi*sum(int2);
            
%             optionType = params('optionType');
            
            switch  optionType
                case 'Call'
                    out = fwd*(p1 + 0.5) - strikePrice*(p2 + 0.5);
                case 'Put'
                    out = fwd*(p1 - 0.5) - strikePrice*(p2 - 0.5);
                otherwise
                    error('not supported! only Call or Put')
            end
                
            
        end
        
        function y = HestonProbRouah(eqHeston,phi,kappa,theta,lambda,rho,sigma,tau,K,S,r,q,v,Pnum,Trap)

                % Returns the integrand for the risk neutral probabilities P1 and P2.
                % phi = integration variable
                % Pnum = 1 or 2 (for the probabilities)
                % Heston parameters:
                %    kappa  = volatility mean reversion speed parameter
                %    theta  = volatility mean reversion level parameter
                %    lambda = risk parameter
                %    rho    = correlation between two Brownian motions
                %    sigma  = volatility of variance
                %    v      = initial variance
                % Option features.
                %    PutCall = 'C'all or 'P'ut
                %    K = strike price
                %    S = spot price
                %    r = risk free rate
                %    Trap = 1 "Little Trap" formulation 
                %           0  Original Heston formulation

                % Log of the stock price.
                x = log(S);

                % Parameter "a" is the same for P1 and P2.
                a = kappa*theta;

                % Parameters "u" and "b" are different for P1 and P2.
                if Pnum==1
                    u = 0.5;
                    b = kappa + lambda - rho*sigma;
                else
                    u = -0.5;
                    b = kappa + lambda;
                end

                d = sqrt((rho*sigma*i*phi - b)^2 - sigma^2*(2*u*i*phi - phi^2));
                g = (b - rho*sigma*i*phi + d) / (b - rho*sigma*i*phi - d);

                if Trap==1
                    % "Little Heston Trap" formulation
                    c = 1/g;
                    D = (b - rho*sigma*i*phi - d)/sigma^2*((1-exp(-d*tau))/(1-c*exp(-d*tau)));
                    G = (1 - c*exp(-d*tau))/(1-c);
                    C = (r-q)*i*phi*tau + a/sigma^2*((b - rho*sigma*i*phi - d)*tau - 2*log(G));
                elseif Trap==0
                    % Original Heston formulation.
                    G = (1 - g*exp(d*tau))/(1-g);
                    C = (r-q)*i*phi*tau + a/sigma^2*((b - rho*sigma*i*phi + d)*tau - 2*log(G));
                    D = (b - rho*sigma*i*phi + d)/sigma^2*((1-exp(d*tau))/(1-g*exp(d*tau)));
                end

                % The characteristic function.
                f = exp(C + D*v + i*phi*x);

                % Return the real part of the integrand.
                y = real(exp(-i*phi*log(K))*f/i/phi);
        end
        
        
        
        function y = HestonPriceGaussLaguerreRouahSimple(eqHeston,PutCall,S,K,T,r,q,kappa,theta,sigma,lambda,v0,rho,trap,x,w)

                % Heston (1993) call or put price by Gauss-Laguerre Quadrature
                % Uses the original Heston formulation of the characteristic function,
                % or the "Little Heston Trap" formulation of Albrecher et al.
                % INPUTS -------------------------------------------------------
                %   PutCall = 'C' Call or 'P' Put
                %   S = Spot price.
                %   K = Strike
                %   T = Time to maturity.
                %   r = Risk free rate.
                %   kappa  = Heston parameter: mean reversion speed.
                %   theta  = Heston parameter: mean reversion level.
                %   sigma  = Heston parameter: volatility of vol
                %   lambda = Heston parameter: risk.
                %   v0     = Heston parameter: initial variance.
                %   rho    = Heston parameter: correlation
                %   trap:  1 = "Little Trap" formulation
                %          0 = Original Heston formulation
                %   x = Gauss Laguerre abscissas
                %   w = Gauss Laguerre weights
                % OUTPUT -------------------------------------------------------
                %   The Heston call or put price

                % Numerical integration
                for k=1:length(x)
                    int1(k) = w(k)*eqHeston.HestonProbRouah(x(k),kappa,theta,lambda,rho,sigma,T,K,S,r,q,v0,1,trap);
                    int2(k) = w(k)*eqHeston.HestonProbRouah(x(k),kappa,theta,lambda,rho,sigma,T,K,S,r,q,v0,2,trap);
                end

                % Define P1 and P2
                P1 = 1/2 + 1/pi*sum(int1);
                P2 = 1/2 + 1/pi*sum(int2);

                % The call price
                HestonC = S*exp(-q*T)*P1 - K*exp(-r*T)*P2;

                % The put price by put-call parity
%                 HestonP = HestonC - S*exp(-q*T) + K*exp(-r*T);
                HestonP = S*exp(-q*T)*(P1-1.0) - K*exp(-r*T)*(P2-1.0);

                % Output the option price
                if strcmp(PutCall,'C')
                    y = HestonC;
                else
                    y = HestonP;
                end
            
        end
        
        function out = HestonPriceGaussLaguerreRouah(eqHeston,spotPrice,strikePrice,termDay,optionType)
       
                term = termDay/365.0;

                fwd = eqHeston.Fwd(spotPrice,termDay);

                impliedRepoRate = log(fwd/spotPrice)/term;

                kappa = eqHeston.kappa;
                theta = eqHeston.theta;
                rho   = eqHeston.rho;

                sigma = eqHeston.sigma;
                v0    = eqHeston.v0;

                x = eqHeston.quadrature_nodesAndWeights(:,1);
                w = eqHeston.quadrature_nodesAndWeights(:,2);
                
                trap = 1;
                switch  optionType
                    case 'Call'
                        out = eqHeston.HestonPriceGaussLaguerreRouahSimple('C',spotPrice,strikePrice,term,impliedRepoRate,0.0,kappa,theta,sigma,0.0,v0,rho,trap,x,w);

                    case 'Put'
                        out = eqHeston.HestonPriceGaussLaguerreRouahSimple('P',spotPrice,strikePrice,term,impliedRepoRate,0.0,kappa,theta,sigma,0.0,v0,rho,trap,x,w);
                    otherwise
                        error('not supported! only Call or Put')
                end
        end
        
        function out = HestonCharacteristicFcnR(eqHeston,phi,kappa,theta,rho,sigma,term,v0)
                                                     
             al  = -phi*phi/2.0 -1i*phi/2.0;
             bet = kappa - rho*sigma*1i*phi;
             gam = sigma*sigma/2.0;
             d   = sqrt(bet*bet -4*al*gam);
             rp  = (bet + d)/(2*gam);
             rm  = (bet - d)/(2*gam);
             g   = rm/rp;
             D   = rm*(1 - exp(-d*term))/(1 - g*exp(-d*term));
             C   = kappa*(rm * term -2/(sigma*sigma) * log((1 - g*exp(-d*term))/(1 - g)));
             out = exp(C*theta + D*v0);
        end
        
        function out = HestonPriceGaussLaguerreGatheralR(eqHeston,spotPrice,strikePrice,termDay,optionType)

            term = termDay/365.0;
            
            fwd = eqHeston.Fwd(spotPrice,termDay);
            
%             impliedRepoRate = log(fwd/spotPrice)/term;
            
            kappa = eqHeston.kappa;
            theta = eqHeston.theta;
            rho   = eqHeston.rho;
            
            sigma = eqHeston.sigma;
            v0    = eqHeston.v0;
            
            x = eqHeston.quadrature_nodesAndWeights(:,1);
            w = eqHeston.quadrature_nodesAndWeights(:,2);
            
            int1 = zeros(length(x),1);
            
            realPart = 0.0;
            charFcn = 0.0;
            
            logK = log(strikePrice/fwd);
            reducedK = strikePrice/fwd; 
            
            for k=1:length(x)
                charFcn = eqHeston.HestonCharacteristicFcnR(x(k) -1i/2.0,kappa,theta,rho,sigma,term,v0);
                realPart = real(exp(-1i*x(k)*logK)*charFcn);
                int1(k) = w(k) * 1.0/(x(k)*x(k) + 0.25)*realPart;                       
            end
            
            p1 = 1/pi*sum(int1);
            
            switch  optionType
                case 'Call'
                    out = fwd*(1.0 - sqrt(reducedK)*p1);
                case 'Put'
                    out = fwd*(reducedK -sqrt(reducedK)*p1);
                otherwise
                    error('not supported! only Call or Put')
            end
                
            
        end
        
        function out = modelOTMPrice(eqHeston,spotPrice,strikePrice,termDay,vanillayOptionType)
                fwd = eqHeston.Fwd(spotPrice,termDay);
                K = strikePrice/fwd;
                if nargin == 4
                    if K <= 1.0
                        optionType = 'Put';
                    else
                        optionType = 'Call';
                    end
                else
                    optionType = vanillayOptionType;
                end
                
                if strcmp(eqHeston.modelPriceFormula,'Rouah')
                    out = eqHeston.HestonPriceGaussLaguerreRouah(spotPrice,strikePrice,termDay,optionType);
                elseif strcmp(eqHeston.modelPriceFormula,'Quantlib')
                    out = eqHeston.HestonPriceGaussLaguerre(spotPrice,strikePrice,termDay,optionType);
                elseif strcmp(eqHeston.modelPriceFormula,'GatheralR')
                    out = eqHeston.HestonPriceGaussLaguerreGatheralR(spotPrice,strikePrice,termDay,optionType);
                else
                    error('unknown modelPriceFormula type')
                end
        end
                
        function out = modelOTMPriceFwdMon(eqHeston,spotPrice,strikePrice,termDay,vanillayOptionType)
%                 fwd = eqHeston.Fwd(spotPrice,termDay);
                fwd = 1.0;
                K = strikePrice/fwd;
                if nargin == 4
                    if K <= 1.0
                        optionType = 'Put';
                    else
                        optionType = 'Call';
                    end
                else
                    optionType = vanillayOptionType;
                end
                
                if strcmp(eqHeston.modelPriceFormula,'Rouah')
                    out = eqHeston.HestonPriceGaussLaguerreRouah(spotPrice,strikePrice,termDay,optionType);
                elseif strcmp(eqHeston.modelPriceFormula,'Quantlib')
                    out = eqHeston.HestonPriceGaussLaguerreFwdMon(spotPrice,strikePrice,termDay,optionType);
                elseif strcmp(eqHeston.modelPriceFormula,'GatheralR')
                    out = eqHeston.HestonPriceGaussLaguerreGatheralR(spotPrice,strikePrice,termDay,optionType);
                else
                    error('unknown modelPriceFormula type')
                end
        end
        
        
        function out = Heston_ImpVol(eqHeston,strike,term)
                K = strike;
                optionType = 'Put';
                if K <= 1.0
                    optionType = 'Put';
                else
                    optionType = 'Call';
                end
                
                modelPrice = eqHeston.modelOTMPriceFwdMon(1.0,strike,term*365.0,optionType);
                model_vol = eqHeston.ImpliedBlackVol(modelPrice,1.0,strike,term);
                out = model_vol;
        end
        
        function out = TDMASolve(eqHeston,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqHeston,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function localVol = GetLocalVolFromProxy(eqHeston,volProxy,Ks,ipos,idxNow)

            localVol = zeros(length(Ks),1);
            volProxyKs = zeros(1,length(volProxy));
            
            fwdMoneyNessPerExpiry = eqHeston.fwdMoneyNess(idxNow,:);
            
            if strcmp(eqHeston.modelParams('LocalVolInterpol') ,'monotonicCubicSpline')
                if strcmp(eqHeston.modelParams('VolProxyOnMarketStrikeYN') ,'Yes')
                    aaa =1.0;
                else
                    for i=1:length(volProxy)
                        volProxyKs(i) = Ks(ipos(i));
                    end

                    localVol = pchip(volProxyKs,volProxy,Ks);
                    %flat extrapolation at the ends
                    for i=1:length(Ks)
                        if Ks(i) <= Ks(ipos(1))
                            localVol(i) = localVol(ipos(1));
                        elseif Ks(i) >= Ks(ipos(length(ipos)))
                            localVol(i) = localVol(ipos(length(ipos)));
                        end
                    end
                end
            elseif strcmp(eqHeston.modelParams('LocalVolInterpol') ,'matlabLinear')
                for i=1:length(volProxy)
                    volProxyKs(i) = Ks(ipos(i));
                end
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end
            elseif strcmp(eqHeston.modelParams('LocalVolInterpol') ,'matlabLinearMarketFwdMoneyness')
                for i=1:length(volProxy)
                    volProxyKs(i) = log(fwdMoneyNessPerExpiry(i));
                end
                
                for i=1:length(Ks)
                    localVol(i) = H_interpolation(volProxyKs,volProxy,Ks(i),1);
                end    
            else
                for i=1: length(volProxy)
    %                 Extrapolation at the left and right
                    if i == 1
                        for j=1:ipos(i)-1
                            localVol(j) = volProxy(i);
                        end
                    elseif i == length(volProxy)
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                        for j=ipos(i):length(Ks)
                            localVol(j) = volProxy(i);
                        end
    %                  linear interpolation in the spot grid in-between    
                    else
                        for j=ipos(i-1):ipos(i)-1
                            localVol(j) = (Ks(j)-Ks(ipos(i-1)))*(volProxy(i)-volProxy(i-1))/(Ks(ipos(i))-Ks(ipos(i-1))) + volProxy(i-1);
                        end
                    end
                end
            end
            
        end
        
        function [newC newP] = Solve1DPDE(eqHeston,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
%             proxy = zeros(length(lastC),1);
            proxy = eqHeston.GetLocalVolFromProxy(tvar,optParams.Ks,optParams.ipos,optParams.idxNow);

%             for i=1: length(tvar)
% %                 Extrapolation at the left and right
%                 if i == 1
%                     for j=1:optParams.ipos(i)-1
%                         proxy(j) = tvar(i);
%                     end
%                 elseif i == length(tvar)
%                     for j=optParams.ipos(i-1):optParams.ipos(i)-1
%                         proxy(j) = (optParams.Ks(j)-optParams.Ks(optParams.ipos(i-1)))*(tvar(i)-tvar(i-1))/(optParams.Ks(optParams.ipos(i))-optParams.Ks(optParams.ipos(i-1))) + tvar(i-1);
%                     end
%                     for j=optParams.ipos(i):length(lastC)
%                         proxy(j) = tvar(i);
%                     end
% %                  linear interpolation in the log grid in-between    
%                 else
%                     for j=optParams.ipos(i-1):optParams.ipos(i)-1
%                         proxy(j) = (optParams.Ks(j)-optParams.Ks(optParams.ipos(i-1)))*(tvar(i)-tvar(i-1))/(optParams.Ks(optParams.ipos(i))-optParams.Ks(optParams.ipos(i-1))) + tvar(i-1);
%                     end
%                 end
%             end
%            
%             proxy(length(lastC)) = tvar(length(tvar));
            
            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            for i=2:tdma.size-1
                temp = 0.5*dT*proxy(i)*proxy(i)/dK;
                tdma.a(i) = -temp*(1/dK + 0.5);
                tdma.b(i) = 1 + 2.0/dK*temp;
                tdma.c(i) = -temp*(1/dK - 0.5);
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqHeston.LUDecompose(tdma);
            pmeshC = eqHeston.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqHeston.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = InterpolateTargetStrikeVol(eqHeston,idxNow,meshC,meshP,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            out.strikes = params.targetStrikes;
            strikeSize = length(params.targetStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            lnK = 0.0;
            for i=1:strikeSize
                K = out.strikes(i);
                lnK = log(K);
                %linear interpolated option values
                NGP = round((lnK-params.Ks(1))/params.dK);
                % corrected distance index
                NGP = NGP +1;
                if NGP < 1
                    NGP = 1;
                elseif NGP >= params.Ns
                    NGP = params.Ns-1;
                end

                alpha = (lnK-params.Ks(NGP))/params.dK;
                cValue = (1-alpha)*meshC(NGP) + alpha*meshC(NGP+1);
                pValue = (1-alpha)*meshP(NGP) + alpha*meshP(NGP+1);
                if K <= 1.0
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K, ...
                                          0.0,params.expiry(idxNow)/365.0,a,b,pValue,Tol,MaxIter);
                     out.interpOTMPrices(i) = pValue;
                else
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K, ...
                                          0.0,params.expiry(idxNow)/365.0,a,b,cValue,Tol,MaxIter);
                    out.interpOTMPrices(i) = cValue;
                end
            end
            
            
        end
        
        function newP = inductPDEBackward(eqHeston,fromTime,toTime,lastP,Ks)
            
            expiry = eqHeston.localVolSurface.expiry;
            
            idx = find(eqHeston.localVolSurface.expiry >= fromTime/365.0);
            if isempty(idx)
                idxNow = length(expiry);
            else
                idxNow = min(idx);
            end
            
            dT = (fromTime - toTime)/365.0;
            oneStepDt = 1.0/365.0;
            NT = round(dT/oneStepDt);
            %filling proxy grid vol
            proxy = zeros(length(lastP),1);
            
            size = length(lastP);
            a = zeros(size,1);
            b = zeros(size,1);
            c = zeros(size,1);
            b_rg = zeros(size,1);
            
            dK = Ks(2) - Ks(1);
            dT = oneStepDt;
            
            newP = lastP;
            for t=1:NT
                idx = find(eqHeston.localVolSurface.expiry >= fromTime/365.0 - (t-1)*oneStepDt);
                if isempty(idx)
                    idxNow = length(expiry);
                else
                    idxNow = min(idx);
                end
                proxy = eqHeston.localVolSurface.localVol(idxNow,:);
                % lognormal case
                for i=1:size
                    temp = 0.5*dT*proxy(i)*proxy(i)/dK;
                    a(i) = -temp*(1/dK + 0.5);
                    b(i) = 1 + 2.0/dK*temp;
                    b_rg(i) = b(i) -1.0;
                    c(i) = -temp*(1/dK - 0.5);
                end

                a(1) = 0;
                c(size) = 0;

                % absorbing boundary condition
                c(1) = 0;
                a(size) = 0;

                b(1) = 1;
                b(size) = 1;
                
                tdma.size = length(lastP);
                tdma.a = a;
                tdma.b = b;
                tdma.c = c;
                tdma.uu = zeros(tdma.size,1);
                tdma.ll = zeros(tdma.size,1);
                tdma.dd = zeros(tdma.size,1);

                tdma.bupdated = 1;

                tdmaLU =  eqHeston.LUDecompose(tdma);
           
                newP = eqHeston.TDMASolve(tdmaLU,newP);
            end
              
        end
        
        
        function out = computeBackwardPDEOne(eqHeston,maturity,strike,params)
            expiry = params.expiry;
            
            modelX = params.Ks;
            modelXSize = length(params.Ks);
            
            mesh = zeros(modelXSize,1);
            Ks = params.Ks;
            
            % put option
            if strike <= 1.0
                for i=1:modelXSize
                    mesh(i,1) = max(strike- exp(modelX(i)),0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqHeston.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,Ks);
                end
                
                out = (1-params.PricingWeight)*mesh(params.PricingIdx) + params.PricingWeight*mesh(params.PricingIdx+1);
                
            else
                % call option
                
                for i=1:modelXSize
                    mesh(i,1) = max(exp(modelX(i))-strike,0);
                end

                volExpiry = expiry(find(expiry <= maturity));
                volExpiry = [volExpiry; 0];
                timeStep = sort(union(volExpiry,maturity),'ascend');
                for i=length(timeStep):-1:2
                    mesh = eqHeston.inductPDEBackward(timeStep(i),timeStep(i-1),mesh,Ks);
                end
                
                out = (1-params.PricingWeight)*mesh(params.PricingIdx) + params.PricingWeight*mesh(params.PricingIdx+1);
                
            end
            
        end
        
        function out = computeBackwardPDEOTMTotal(eqHeston,params)
            expiry = params.expiry;
%             strike = params.strike;
            strike = params.fwdMoneyNess;
            
            pdeOTMPrices =  zeros(length(expiry),length(strike));
            for i=1:length(expiry)
%                 strikePerExpiry = strikes(i,:);
                strikePerExpiry = strike(i,:);
%                 strikePerExpiry = params.fwdMoneyness(i,:);
                for j=1:length(strikePerExpiry)
                    pdeOTMPrices(i,j) = eqHeston.computeBackwardPDEOne(expiry(i),strikePerExpiry(j),params);
                end
            end
            
            out = pdeOTMPrices;
            
        end
        
         % NM : nearest month forward
        function out = CommoFwdNM(eqHeston,observeTime)
            modelStates = eqHeston.localVolSurface.Ks;
            forwardCurve = eqHeston.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * exp(modelStates(i)); 
             end
             
             out = stochasticFwd;
        end
        
        function out = computeStepdown1SPDE(eqHeston,valueDate,stepdownParams)
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqHeston.localVolSurface.expiry;
            expiryD =  expiry*365;
            volExpiry = expiryD(find(expiryD <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
                
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           
           modelStates = eqHeston.localVolSurface.Ks;
           
           modelStatesSize = length(modelStates);
           
           %down barrier touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           currentTime = timeStep(totalTimeStepSize);
           currentTimeIdx = totalTimeStepSize;
           currentNodeIdx = scheduleSize;
           
           comFwd = eqHeston.CommoFwdNM(currentTime);
           strikeMat = autoCallSchedule.strike(scheduleSize);
           couponMat = autoCallSchedule.coupon(scheduleSize);
           
%            strikeOH = strikeMat + overHedgeShift;
           % samsung overhedge payoff
           if strcmp(SSpayoffYN,'YES')
               for i=1:modelStatesSize
                   if comFwd(i) < basePrice*callStrike1
                        payoffStateA.cashflow(i) = nominal * callValue1/callStrike1* comFwd(i)/basePrice; 
                   elseif comFwd(i) < basePrice*strikeMat 
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat - callValue1)/(strikeMat-callStrike1)*(comFwd(i)/basePrice - callStrike1) + nominal*callValue1; 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
               
           else
               for i=1:modelStatesSize
                   if comFwd(i) >= basePrice*strikeMat
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat); 
                   else
                       payoffStateA.cashflow(i) = nominal * (1.0 + couponMat + (comFwd(i)/basePrice-strikeMat)*overHedgeSpread);
                       payoffStateA.cashflow(i) = max(payoffStateA.cashflow(i),nominal * comFwd(i)/basePrice);
                   end
               end

               payoffStateB.cashflow = payoffStateA.cashflow;

               for i=1:modelStatesSize
                    if comFwd(i) > basePrice*lowerBarrier
                        payoffStateB.cashflow(i) = nominal * (1.0 + couponMat);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqHeston.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            hitValue.payoff = payoffStateA.cashflow_npv;
            
            unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            unhitValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
           
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
                
                endTimeIdx = endTimeIdx + 1;
            %% induction start
                mesh = hitValue.payoff;
                meshB = unhitValue.payoff;
                for idx= startTimeIdx:-1:endTimeIdx
                    mesh  = inductPDEBackward(eqHeston,timeStep(idx),timeStep(idx-1),mesh,modelStates);
                    meshB = inductPDEBackward(eqHeston,timeStep(idx),timeStep(idx-1),meshB,modelStates);
%                     mesh  = inductGFBackward(eqHeston,timeStep(idx),timeStep(idx-1),mesh);
%                     meshB = inductGFBackward(eqHeston,timeStep(idx),timeStep(idx-1),meshB);
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx -1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqHeston.CommoFwdNM(currentTime);
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           meshB(j) = mesh(j); 
                        end
                    end
                end
                
                hitValue.payoff = mesh;
                unhitValue.payoff = meshB;
                nMFuture.payoff = comFwd;
              %% induction end
                
                % backward induction in the payoff script
                currentNodeIdx = currentNodeIdx -1;
              %% AtDate operation on Early ExerciseDate
                
                if i > lastAliveExeriseIdx
                    currentTime = timeStep(lastTimeIdx);
                    onePayoffD = eqHeston.zeroCurve.DF(currentTime/365.0);
                    contiValue  = hitValue.payoff/onePayoffD;
                    contiValueB = unhitValue.payoff/onePayoffD;
                    
                    %AutoCall applied
                    comFwd = eqHeston.CommoFwdNM(currentTime);
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                     % intermediate variables
                    payoffStateA.cashflow = zeros(modelStatesSize,1);
                    payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateB.cashflow = zeros(modelStatesSize,1);
                    payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
                    
                    payoffStateC.cashflow = zeros(modelStatesSize,1);
                    payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
                    
                    % samsung overhedge payoff
                    if strcmp(SSpayoffYN,'YES')
                        for j=1:modelStatesSize
                            if comFwd(j)/basePrice >= strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            elseif comFwd(j)/basePrice >= strikeEarly - couponEarly/overHedgeSpread
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j)); 
                            else
%                                 payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
%                                 payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
% 
%                                 payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
%                                 payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                                
                                payoffStateA.cashflow(j) = contiValue(j);
                                payoffStateB.cashflow(j) = contiValueB(j);
                           end
                        end
                    else
                        for j=1:modelStatesSize
                            if comFwd(j) >= basePrice*strikeEarly
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly);
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly);
                            else
                               payoffStateA.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateA.cashflow(j) = max(payoffStateA.cashflow(j),contiValue(j));
                               payoffStateB.cashflow(j) = nominal * (1.0 + couponEarly + (comFwd(j)/basePrice-strikeEarly)*overHedgeSpread);
                               payoffStateB.cashflow(j) = max(payoffStateB.cashflow(j),contiValueB(j));
                           end
                        end
                        
                    end
                    % barrier
                    for j=1:modelStatesSize
                        if comFwd(j) <= basePrice*lowerBarrier
                           payoffStateB.cashflow(j) = payoffStateA.cashflow(j);
                        end
                    end
                    
                    payoffStateC.cashflow = comFwd;
                    
                    for j=1:modelStatesSize
                        payoffStateA.cashflow_npv(j) = payoffStateA.cashflow(j)*onePayoffD;
                        payoffStateB.cashflow_npv(j) = payoffStateB.cashflow(j)*onePayoffD;
                        payoffStateC.cashflow_npv(j) = payoffStateC.cashflow(j)*1.0;
                    end
                    
                    %process payoff at early exercise date
                    hitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
                    hitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
                    hitValue.payoff = payoffStateA.cashflow_npv;
                    
                    unhitValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
                    unhitValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
                    unhitValue.payoff = payoffStateB.cashflow_npv;
                    
                    nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
                    nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
                    nMFuture.payoff = payoffStateC.cashflow_npv;
                    
                end
                   
           end
           
           PricingIdx = eqHeston.localVolSurface.PricingIdx;
           PricingWeight = eqHeston.localVolSurface.PricingWeight;
           
           hitValue.npv = (1-PricingWeight)*hitValue.payoff(PricingIdx) + PricingWeight*hitValue.payoff(PricingIdx+1);
           unhitValue.npv = (1-PricingWeight)*unhitValue.payoff(PricingIdx) + PricingWeight*unhitValue.payoff(PricingIdx+1);
           nMFuture.npv = (1-PricingWeight)*nMFuture.payoff(PricingIdx) + PricingWeight*nMFuture.payoff(PricingIdx+1);
           
%            hitValue.npv = hitValue.payoff(PricingIdx);
%            unhitValue.npv = unhitValue.payoff(PricingIdx);
%            nMFuture.npv = nMFuture.payoff(PricingIdx);
           
           out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = CalculateTarget(eqHeston,idxNow,meshC,meshP,optParams)
            % Calculate Object Function
            
            out.dupireOTMPrice = zeros(optParams.strikeSize,1);
            out.re = zeros(optParams.strikeSize,1);
            
            for i=1:optParams.strikeSize
                K = optParams.marketStrikes(i);
                %linear interpolated option values
%                 NGP = round((K-optParams.Ks(1))/optParams.dK);
                NGP = floor((K-optParams.Ks(1))/optParams.dK);
                % corrected distance index
                NGP = NGP +1;
                if NGP < 1
                    NGP = 1;
                elseif NGP >= optParams.meshSize
                    NGP = optParams.meshSize-1;
                end

                alpha = (K-optParams.Ks(NGP))/optParams.dK;
                cValue = (1-alpha)*meshC(NGP) + alpha*meshC(NGP+1);
                pValue = (1-alpha)*meshP(NGP) + alpha*meshP(NGP+1);
                if K <= 0
                    out.re(i) = pValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                    out.dupireOTMPrice(i) = pValue;
                else
                    out.re(i) = cValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                    out.dupireOTMPrice(i) = cValue;
                end
            end
            
            
        end
        
        function  out  = TargetFunctionVolProxyLevMar(tvar,eqHeston,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            %filling vol proxy grid with the tvar
          %% Solve  Forward PDE One time
            [newC newP] = eqHeston.Solve1DPDE(tvar,mkt_dT,optParams.dK,optParams.lastC,optParams.lastP,optParams);
            optParams.meshC = newC;
            optParams.meshP = newP;
           %% PDE Solve End
            target = CalculateTarget(eqHeston,idxNow,newC,newP,optParams);
            out = target.re;
        end
        
        function  out  = TargetFunctionVolProxy(eqHeston,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            %filling vol proxy grid with the tvar
          %% Solve  Forward PDE One time
            [newC newP] = eqHeston.Solve1DPDE(tvar,mkt_dT,optParams.dK,optParams.lastC,optParams.lastP,optParams);
            optParams.meshC = newC;
            optParams.meshP = newP;
           %% PDE Solve End
            target = CalculateTarget(eqHeston,idxNow,newC,newP,optParams);
            out = 0.0;
            for i=1:length(target.re)
                out = out + target.re(i)*target.re(i);
            end
        end
        
        function  out  = TargetFunctionVolProxyOld(eqHeston,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            %filling vol proxy grid with the tvar
            proxy = zeros(optParams.meshSize,1);
            
            for i=1: optParams.strikeSize
                if i == 1
                    for j=1:optParams.ipos(i)-1
                        proxy(j) = tvar(i);
                    end
                elseif i == optParams.strikeSize
                    for j=optParams.ipos(i-1):optParams.ipos(i)-1
                        proxy(j) = tvar(i);
                    end 
                else
                    for j=optParams.ipos(i-1):optParams.ipos(i)-1
                        proxy(j) = tvar(i);
                    end
                end
            end
           
            proxy(optParams.meshSize) = tvar(optParams.strikeSize);
            
            % Solve  Forward PDE One time
            optParams.meshC = optParams.lastCurveC;
            optParams.meshP = optParams.lastCurveP;
            
            tdma.size = optParams.meshSize;
            tdma.bupdated = 0;
            tdma.a = zeros(optParams.meshSize,1);
            tdma.b = zeros(optParams.meshSize,1);
            tdma.c = zeros(optParams.meshSize,1);
            tdma.uu = zeros(optParams.meshSize,1);
            tdma.ll = zeros(optParams.meshSize,1);
            tdma.dd = zeros(optParams.meshSize,1);
            
            for i=2:optParams.meshSize-1
                temp = 0.5*mkt_dT*proxy(i)*proxy(i)/optParams.dK;
                tdma.a(i) = -temp*(1/optParams.dK + 0.5);
                tdma.b(i) = 1 + 2.0/optParams.dK*temp;
                tdma.c(i) = -temp*(1/optParams.dK - 0.5);
            end
            
            tdma.a(1) = 0;
            tdma.a(optParams.meshSize) = 0;
            tdma.c(1) = 0;
            tdma.c(optParams.meshSize) = 0;
            tdma.b(1) = 1;
            tdma.b(optParams.meshSize) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqHeston.LUDecompose(tdma);
            pmeshC = eqHeston.TDMASolve(tdmaLU,optParams.meshC);
            optParams.meshC = pmeshC;
            
            pmeshP = eqHeston.TDMASolve(tdmaLU,optParams.meshP);
            optParams.meshP = pmeshP;
            % PDE Solve End
         
            % Calculate Object Function
            target = zeros(optParams.strikeSize,1);
         
            for i=1:optParams.strikeSize
                K = optParams.marketStrikes(i);
                %linear interpolated option values
                NGP = round((K-optParams.Ks(1))/optParams.dK);
                % corrected distance index
                NGP = NGP +1;
                if NGP < 1
                    NGP = 1;
                elseif NGP >= optParams.meshSize
                    NGP = optParams.meshSize-1;
                end

                alpha = (K-optParams.Ks(NGP))/optParams.dK;
                cValue = (1-alpha)*optParams.meshC(NGP) + alpha*optParams.meshC(NGP+1);
                pValue = (1-alpha)*optParams.meshP(NGP) + alpha*optParams.meshP(NGP+1);
                optParams.callCurve(i) = cValue;
                optParams.putCurve(i) = pValue;
                if K <= 0
                    target(i) = pValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                else
                    target(i) = cValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                end
            end
            
            out = 0;
            for i=1:optParams.strikeSize
                out = out + target(i)*target(i)*10000;
            end
        end
        
        function bootStrapOut = FindVolProxy(eqHeston,idxNow,dT,lastC,lastP,params)
            %initialize calibration parameters
            
            for i=1:params.strikeSize
%                 tvar(i) = params.volSurface.vol(params.expiry(idxNow),params.strike(i));
                tvar(i) = params.blackVol(idxNow,i);
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            optParams.meshC = zeros(params.Ns,1);
            optParams.meshP = zeros(params.Ns,1);
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrice = params.blackOTMPrice;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
            if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
                % market strike points in fwd PDE grid
                fwdFactor = eqHeston.FwdFactor(params.expiry(idxNow));
                for i=1:params.strikeSize
                    optParams.marketStrikes(i) = log(params.strike(i)/fwdFactor);
                end
            elseif strcmp(params.volSurface.params('moneyNessType'),'deltaFwdMoneyNess')
                for i=1:params.strikeSize
                    optParams.marketStrikes(i) = log(params.fwdMoneyNess(idxNow,i));
                end
            else
                for i=1:params.strikeSize
                    optParams.marketStrikes(i) = log(params.strike(i));
                end
            end
            
            
%             for i=1:params.strikeSize
%                 optParams.marketStrikes(i) = log(params.fwdMoneyness(idxNow,i));
%             end
            
            % positions to separate vol proxy regimes
%             for i=1:params.strikeSize
%                 optParams.ipos(i) = round( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK);
%             end
            if strcmp(eqHeston.modelParams('applyDWLinearInterpol'),'YES')
                for i=1:params.strikeSize
                    optParams.ipos(i) = round( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;
                end
            else
                for i=1:params.strikeSize
                    optParams.ipos(i) = floor( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK) + 1;
                end
                
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastC = lastC;
            optParams.lastP = lastP;
            
            targetfun = @(tvar) TargetFunctionVolProxy(eqHeston,tvar,optParams);
%             options=optimset('Algorithm','trust-region-reflective');
%             [x, fval] = fmincon(targetfun,tvar,[],[],[],[],lb,ub,[]);
%             [x, fval] = fminsearch(targetfun,tvar);
            
%             [x, fval] = fmincon(targetfun,tvar,[],[],[],[],lb,ub,[],options);
%             [x,fval,exitflag,output1,lambda,grad,hessian] = fmincon(targetfun,tvar,[],[],[],[],lb,ub,[],options);

            options=[1E-03, 1E-25, 1E-25, 1E-25, 1E-25];
            x=  zeros(params.strikeSize,1);
            [ret, popt, info, covar]=levmar('TargetFunctionVolProxyLevMar1',tvar,x, 200, options,'unc',eqHeston,optParams);
            %Levenberg Marquardt Algorithm
            
%             targetfun = @(tvar) TargetFunctionVolProxyLevMar(eqHeston,tvar,optParams);
%             options=optimset('Algorithm','levenberg-marquardt');
%             [x, fval] = lsqnonlin(targetfun,tvar,lb,ub,options);
%             
%             targetfun = @(t) eqHeston.TargetFunctionVolProxyLevMar(t,optParams);
%             t0 = tvar;
%             options=optimset('Algorithm','levenberg-marquardt');
%             [x, fval] = lsqnonlin(targetfun,tvar,lb,ub,options);
%             x = zeros(1,params.strikeSize);
%             options=[1E-03, 1E-15, 1E-15, 1E-20, 1E-06];
% %             [ret, x, info]=levmar('targetfun', t0, x, 200, options, optParams);
%             [ret, popt, info]=levmar('targetfun', t0, x, 200, options);
            
            
            % min vol 0.0001
            minVol = 0.0001;
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = max(popt(i),minVol);
%                 bootStrapOut.volProxy(i) = popt(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            [newC newP] = eqHeston.Solve1DPDE(bootStrapOut.volProxy,dT,optParams.dK,lastC,lastP,optParams);
            target = eqHeston.CalculateTarget(idxNow,newC,newP,optParams);
            
            bootStrapOut.lastC = newC;
            bootStrapOut.lastP = newP;
            
            bootStrapOut.re = target.re;
            bootStrapOut.dupireOTMPrice = target.dupireOTMPrice;
            
        end
        
        function mcmcOut = inductMCForwardEuler(eqHeston,fromTime,toTime,lastX,lastV,Zs,Zv)
            
            % Zs , Zv are independent normal browninan motion
            
            predictorS = lastX;
            predictorV = lastV;
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            
            kappa = eqHeston.kappa;
            theta = eqHeston.theta;
            sigma = eqHeston.sigma;
            v0    = eqHeston.kappa;
            rho   = eqHeston.rho;
            
            
            for i=1:length(lastX)
                predictorV(i) = lastV(i) + kappa*(theta - lastV(i))*Dt + sigma*sqrt(lastV(i)*Dt)*Zv(i);
                % full truncation for variance process
                predictorV(i) = max(predictorV(i),0.0);
                
                Zsc = rho*Zv(i) + sqrt(1.0-rho^2)*Zs(i);
                predictorS(i) = lastX(i)*exp(-0.5*lastV(i)*Dt + sqrt(lastV(i)*Dt)*Zsc);
            end
            
            mcmcOut.nextX = predictorS;
            mcmcOut.nextV = predictorV;
        end
        
        function mcmcOut = inductMCForwardMilstein(eqHeston,fromTime,toTime,lastX,lastV,Zs,Zv)
            
            % Zs , Zv are independent normal browninan motion
            
            predictorS = lastX;
            predictorV = lastV;
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            
            kappa = eqHeston.kappa;
            theta = eqHeston.theta;
            sigma = eqHeston.sigma;
            v0    = eqHeston.kappa;
            rho   = eqHeston.rho;
            
            
            for i=1:length(lastX)
                predictorV(i) = lastV(i) + kappa*(theta - lastV(i))*Dt + sigma*sqrt(lastV(i)*Dt)*Zv(i) ...
                                + 0.25*sigma^2*Dt*(Zv(i)^2-1);
                % full truncation for variance process
                predictorV(i) = max(predictorV(i),0.0);
                
                Zsc = rho*Zv(i) + sqrt(1.0-rho^2)*Zs(i);
                predictorS(i) = lastX(i)*exp(-0.5*lastV(i)*Dt + sqrt(lastV(i)*Dt)*Zsc);
            end
            
            mcmcOut.nextX = predictorS;
            mcmcOut.nextV = predictorV;
        end
        
        function mcmcOut = inductMCForwardNCCS(eqHeston,fromTime,toTime,lastX,lastV,Zs,Zv)
            
            % for Variance Process we sample from the Noncentral Chi Square Distribution
            % Zs , Zv are independent normal browninan motion
            
            predictorS = lastX;
            predictorV = lastV;
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            
            % Andersen's Quadratic Exponential Settings
            gamma1 = 0.5;
            gamma2 = 0.5;
            phic = 1.5;
%             ApplyMCYN = 'YES';
            ApplyMCYN = 'NO';
            
            kappa = eqHeston.kappa;
            theta = eqHeston.theta;
            sigma = eqHeston.sigma;
            v0    = eqHeston.kappa;
            rho   = eqHeston.rho;
            
            % Parameters for the QE scheme
            E = exp(-kappa*Dt);  % Simplify the coding
            K0 = -kappa*rho*theta*Dt/sigma;
            K1 = (kappa*rho/sigma - 1/2)*gamma1*Dt - rho/sigma;
            K2 = (kappa*rho/sigma - 1/2)*gamma2*Dt + rho/sigma;
            K3 = gamma1*Dt*(1-rho^2);
            K4 = gamma2*Dt*(1-rho^2);
            A = K2 + K4/2;
            
            C = sigma^2*(1-E)/(4*kappa);
            dim = 4*kappa*theta/(sigma^2);
            Dorg = 4*kappa*E/(sigma^2)/(1-E);
            D = Dorg*lastV;
            predictorV = C * ncx2rnd(dim,D,length(lastX),1);
            for i=1:length(lastX)
%                 Uv = normcdf(Zv(i));
%                 D = Dorg*lastV(i);
                
%                 predictorV(i) = C * ncx2inv(Uv,dim,D);
                % Martingale Correction
                if (strcmp(ApplyMCYN,'YES')) && (A < 1/(2*C))
                    M = exp(A*Dorg*C/(1-2*A*C))/(sqrt(1-2*A*C))^(dim);
                    K0 = -log(M) - (K1 + 0.5*K3)*lastV(i);
                end
                    
                predictorS(i) = lastX(i)*exp(K0+K1*lastV(i) + K2*predictorV(i) + ...
                                sqrt(K3*lastV(i)+K4*predictorV(i))*Zs(i));
                
            end
            
            mcmcOut.nextX = predictorS;
            mcmcOut.nextV = predictorV;
        end
        
        function mcmcOut = inductMCForwardQE(eqHeston,fromTime,toTime,lastX,lastV,Zs,Zv)
            
            % U (NMC,numOfFactors)  independent brownian motion
            
            % Zs , Zv are independent normal browninan motion
            
            predictorS = lastX;
            predictorV = lastV;
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            
            % Andersen's Quadratic Exponential Settings
            gamma1 = 0.5;
            gamma2 = 0.5;
            phic = 1.5;
%             ApplyMCYN = 'YES';
            ApplyMCYN = 'NO';
            
            kappa = eqHeston.kappa;
            theta = eqHeston.theta;
            sigma = eqHeston.sigma;
            v0    = eqHeston.kappa;
            rho   = eqHeston.rho;
            
            % Parameters for the QE scheme
            E = exp(-kappa*Dt);  % Simplify the coding
            K0 = -kappa*rho*theta*Dt/sigma;
            K1 = (kappa*rho/sigma - 1/2)*gamma1*Dt - rho/sigma;
            K2 = (kappa*rho/sigma - 1/2)*gamma2*Dt + rho/sigma;
            K3 = gamma1*Dt*(1-rho^2);
            K4 = gamma2*Dt*(1-rho^2);
            A = K2 + K4/2;
            
            for i=1:length(lastX)
                m  = theta + (lastV(i) - theta)*E;
                s2 = lastV(i)*sigma^2*E/kappa*(1-E) + theta*sigma^2/2/kappa*(1-E)^2;
                phi = s2/m^2;
                
                if phi <= phic
                    % moment matching for large variance nonCentral Chi
                    % Square Distribution
                    % large variance -> large noncentrality
                    b = sqrt(2/phi -1 + sqrt(2/phi*(2/phi-1)));
                    a = m/(1+b^2);
                    predictorV(i) = a*(b+Zv(i))^2;
                    % Martingale Correction
                    if (strcmp(ApplyMCYN,'YES')) && (A < 1/(2*a))
                        M = exp(A*b^2*a/(1-2*A*a))/sqrt(1-2*A*a);
                        K0 = -log(M) - (K1 + 0.5*K3)*lastV(i);
                    end
                    
                    predictorS(i) = lastX(i)*exp(K0+K1*lastV(i) + K2*predictorV(i) + ...
                                    sqrt(K3*lastV(i)+K4*predictorV(i))*Zs(i));
                    
                else
                    % moment matching for small variance
                    p = (phi -1)/(phi +1);
                    beta = (1-p)/m;
                    Uv = normcdf(Zv(i));
                    if (0.0 <= Uv) && (Uv <= p)
                        phiinv = 0.0;
                    elseif (p < Uv) && (Uv <=1)
                        phiinv = 1/beta*log((1-p)/(1-Uv));
                    end
                    predictorV(i) = phiinv;
                    % Martingale Correction
                    if (strcmp(ApplyMCYN,'YES')) && (A < beta)
                        M = p + beta*(1-p)/(beta -A);
                        K0 = -log(M) -(K1 + 0.5*K3)*lastV(i);
                    end
                    
                    predictorS(i) = lastX(i)*exp(K0+K1*lastV(i) + K2*predictorV(i) + ...
                                    sqrt(K3*lastV(i)+K4*predictorV(i))*Zs(i));
                end
                
            end
            
            mcmcOut.nextX = predictorS;
            mcmcOut.nextV = predictorV;
        end
        
        function out = EQFwdMC(eqHeston,observeTime,modelStates)
            spotPrice = eqHeston.spot.params('rawData');
            detFwd = eqHeston.Fwd(spotPrice,observeTime); 

             %stochasticFwd(0,T)
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);

             for i=1:stateSize
                stochasticFwd(i) = detFwd * modelStates(i); 
             end

             out = stochasticFwd;
        end
        
        function out = BarrierCheck(eqHeston,comFwd,isKI,payoffInfo)
            basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            modelStatesSize = length(comFwd);
            out = zeros(modelStatesSize,1);
            for idx=1:modelStatesSize
                if (isKI(idx) > 0) || (comFwd(idx) <= basePrice*lowerBarrier)
                    out(idx) = 1.0;
                end
            end
        end
        
        function out = computeVanillaMC(eqHeston,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
%             Pricingidx = eqHeston.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
%             expiry = eqHeston.localVolSurface.expiry;
            if isfield(eqHeston.localVolSurface,'expiry')
                expiry = eqHeston.localVolSurface.expiry;
            else
                expiry = eqHeston.localVolSurface.maturities;
            end
            
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqHeston.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqHeston.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqHeston.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                numOfFactors = 2;
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqHeston.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
               
%                % correlate brownian motion
%                rho = eqHeston.rho;
%                UTemp = U;
%                
%                for i=1:totalTimeStepsSize-1
%                    U(:,2*(i-1)+1) = sqrt(1-rho^2)*UTemp(:,2*(i-1)+1) + rho*UTemp(:,2*(i-1)+2);
%                    U(:,2*(i-1)+2) =                                    1.0*UTemp(:,2*(i-1)+2); 
%                end
            else
                rng('default');
                rng(0);
                
                NMC = eqHeston.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                numOfFactors = 2;
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
%                 % correlate brownian motion
%                 % correlate brownian motion
%                 rho = eqHeston.rho;
%                 UTemp = U;
%                
%                 for i=1:totalTimeStepsSize-1
%                     U(:,2*(i-1)+1) = sqrt(1-rho^2)*UTemp(:,2*(i-1)+1) + rho*UTemp(:,2*(i-1)+2);
%                     U(:,2*(i-1)+2) =                                    1.0*UTemp(:,2*(i-1)+2); 
%                 end

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           %  X  = S(t)/F(0,t)  : spot process
           %  V  = instantaneous variance proces
           
           initX = ones(NMC,1);
           initV = ones(NMC,1)*eqHeston.v0;
           
           nextX = initX;
           nextV = initV;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
           strike =  vanillaParams.params('strike');
%            modelStates = eqHeston.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
%                 Ks = eqHeston.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardQE(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    if strcmp(eqHeston.modelParams('MCScheme'), 'Euler')
                        mcmcOut   = inductMCForwardEuler(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'Milstein')
                        mcmcOut   = inductMCForwardMilstein(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'QE')
                        mcmcOut   = inductMCForwardQE(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'NonCentralChiSquare')
                        mcmcOut   = inductMCForwardNCCS(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    else
                        error('unImplemented MC Scheme');
                    end
                    
                    
                    nextX = mcmcOut.nextX;
                    nextV = mcmcOut.nextV;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqHeston.EQFwdMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i) - strike,0);
                    payoffStateB.cashflow(i) = max(comFwd(i) - strike,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i) + strike,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i) + strike,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqHeston.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            Pricingidx = eqHeston.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeBarrierMC(eqHeston,valueDate,barrierParams)
            % model schedule generation
            expiryDate = H_Date(barrierParams.endDate);
            scheduleSize = 1;
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
%             Pricingidx = eqHeston.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
%             expiry = eqHeston.localVolSurface.expiry;
            if isfield(eqHeston.localVolSurface,'expiry')
                expiry = eqHeston.localVolSurface.expiry;
            else
                expiry = eqHeston.localVolSurface.maturities;
            end
            
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(barrierParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqHeston.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            for i= scheduleSize:-1:lastAliveExerciseIdx
                idx = find(timeStep == maturity);
                eventTimeIdx(i) = min(idx);
            end
            
            %% MC init 
            useQuasiRandomYN = eqHeston.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqHeston.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                numOfFactors = 2;
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqHeston.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
               
%                % correlate brownian motion
%                rho = eqHeston.rho;
%                UTemp = U;
%                
%                for i=1:totalTimeStepsSize-1
%                    U(:,2*(i-1)+1) = sqrt(1-rho^2)*UTemp(:,2*(i-1)+1) + rho*UTemp(:,2*(i-1)+2);
%                    U(:,2*(i-1)+2) =                                    1.0*UTemp(:,2*(i-1)+2); 
%                end
            else
                rng('default');
                rng(0);
                
                NMC = eqHeston.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                numOfFactors = 2;
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
%                 % correlate brownian motion
%                 % correlate brownian motion
%                 rho = eqHeston.rho;
%                 UTemp = U;
%                
%                 for i=1:totalTimeStepsSize-1
%                     U(:,2*(i-1)+1) = sqrt(1-rho^2)*UTemp(:,2*(i-1)+1) + rho*UTemp(:,2*(i-1)+2);
%                     U(:,2*(i-1)+2) =                                    1.0*UTemp(:,2*(i-1)+2); 
%                 end

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           %  X  = S(t)/F(0,t)  : spot process
           %  V  = instantaneous variance proces
           
           initX = ones(NMC,1);
           initV = ones(NMC,1)*eqHeston.v0;
           
           nextX = initX;
           nextV = initV;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
          %% payoff at maturity
           nominal = barrierParams.params('nominal');
           basePrice = barrierParams.params('basePrice');
           strike =  barrierParams.params('strike');
           lowerBarrier = barrierParams.params('lowerBarrier');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.strike = strike;
           
           KIYN = barrierParams.params('KIYN');
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;

            if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
            % check whether current future price breach the barrier
           comFwd = eqHeston.EQFwdMC(currentTime,nextX);
           isKI = eqHeston.BarrierCheck(comFwd,isKI,payoffInfo);
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                startTimeIdx = 1; % valueDate
                endTimeIdx = eventTimeIdx(i);  
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
%                 Ks = eqHeston.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardQE(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    if strcmp(eqHeston.modelParams('MCScheme'), 'Euler')
                        mcmcOut   = inductMCForwardEuler(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'Milstein')
                        mcmcOut   = inductMCForwardMilstein(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'QE')
                        mcmcOut   = inductMCForwardQE(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'NonCentralChiSquare')
                        mcmcOut   = inductMCForwardNCCS(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    else
                        error('unImplemented MC Scheme');
                    end
                    
                    
                    nextX = mcmcOut.nextX;
                    nextV = mcmcOut.nextV;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqHeston.EQFwdMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqHeston,comFwd,isKI,payoffInfo);
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
            end
           
           comFwd = eqHeston.EQFwdMC(currentTime,nextX);
           isKI = BarrierCheck(eqHeston,comFwd,isKI,payoffInfo);
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           if strcmp(barrierParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    if isKI(i)
                        payoffStateA.cashflow(i) = nominal*max(comFwd(i)/basePrice - strike,0);
                        payoffStateB.cashflow(i) = nominal*max(comFwd(i)/basePrice - strike,0);
                    end
               end
           else
               for i=1:modelStatesSize
                    if isKI(i)
                        payoffStateA.cashflow(i) = nominal*max(-comFwd(i)/basePrice + strike,0);
                        payoffStateB.cashflow(i) = nominal*max(-comFwd(i)/basePrice + strike,0);
                    end
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
           df_ep = eqHeston.zeroCurve.DF(currentTime/365.0);
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            Pricingidx = eqHeston.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeForwardStartingVanillaMC(eqHeston,valueDate,vanillaParams)
            % model schedule generation
            expiryDate = H_Date(vanillaParams.params('maturityDate'));
            startDate  = H_Date(vanillaParams.params('startDate'));
            
            scheduleSize = 2;
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            daysToReset = DateDiff(startDate,valueDate);
            
            if maturity <=0
                out = 0;
                return;
            end
            
%             Pricingidx = eqHeston.localVolSurface.Pricingidx;
            
            expiredChance = 0;
            aliveChance = 0;
%             expiry = eqHeston.localVolSurface.expiry;
            expiry = eqHeston.localVolSurface.expiry;
            
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(vanillaParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqHeston.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            timeStep = sort(union(timeStep,daysToReset),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            lastAliveExerciseIdx = 1;
            
            eventTimeIdx(1) = find(timeStep == daysToReset);
            eventTimeIdx(2) = find(timeStep == maturity);
            
%             for i= scheduleSize:-1:lastAliveExerciseIdx
%                 idx = find(timeStep == maturity);
%                 eventTimeIdx(i) = min(idx);
%             end
            
            %% MC init 
            useQuasiRandomYN = eqHeston.modelParams('useQuasiRandomYN');
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqHeston.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                numOfFactors = 2;
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqHeston.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
               
               
%                % correlate brownian motion
%                rho = eqHeston.rho;
%                UTemp = U;
%                
%                for i=1:totalTimeStepsSize-1
%                    U(:,2*(i-1)+1) = sqrt(1-rho^2)*UTemp(:,2*(i-1)+1) + rho*UTemp(:,2*(i-1)+2);
%                    U(:,2*(i-1)+2) =                                    1.0*UTemp(:,2*(i-1)+2); 
%                end
            else
                rng('default');
                rng(0);
                
                NMC = eqHeston.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                numOfFactors = 2;
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';
                
%                 % correlate brownian motion
%                 % correlate brownian motion
%                 rho = eqHeston.rho;
%                 UTemp = U;
%                
%                 for i=1:totalTimeStepsSize-1
%                     U(:,2*(i-1)+1) = sqrt(1-rho^2)*UTemp(:,2*(i-1)+1) + rho*UTemp(:,2*(i-1)+2);
%                     U(:,2*(i-1)+2) =                                    1.0*UTemp(:,2*(i-1)+2); 
%                 end

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           %  X  = S(t)/F(0,t)  : spot process
           %  V  = instantaneous variance proces
           
           initX = ones(NMC,1);
           initV = ones(NMC,1)*eqHeston.v0;
           
           nextX = initX;
           nextV = initV;
           
          %% grid generation based on basePrice
            
           
          %% payoff at maturity
          relativeStrike =  vanillaParams.params('relativeStrike');
           
           detFwdReset    = eqHeston.FwdFactor(daysToReset);
           detFwdMaturity = eqHeston.FwdFactor(maturity);
           
           fwdRatio = detFwdMaturity/detFwdReset;
           
           reSetS = zeros(NMC,1);
           
%            strike =  vanillaParams.params('strike');
%            modelStates = eqHeston.localVolSurface.Ks;
           modelStatesSize = NMC;
           
           %europeanValue
           europeanValue.npv = 0;
           europeanValue.payoff = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           europeanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           %americanValue
           americanValue.npv = 0;
           americanValue.payoff = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow = zeros(modelStatesSize,1);
           americanValue.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,1);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
%            currentTime = timeStep(totalTimeStepSize);
%            currentTimeIdx = totalTimeStepSize;
%            currentNodeIdx = scheduleSize;
           
            for i=lastAliveExerciseIdx:1:scheduleSize
                % past schedule neglect
                if i== lastAliveExerciseIdx
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                else
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                end
                                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
%                 Ks = eqHeston.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardQE(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    if strcmp(eqHeston.modelParams('MCScheme'), 'Euler')
                        mcmcOut   = inductMCForwardEuler(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'Milstein')
                        mcmcOut   = inductMCForwardMilstein(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'QE')
                        mcmcOut   = inductMCForwardQE(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'NonCentralChiSquare')
                        mcmcOut   = inductMCForwardNCCS(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    else
                        error('unImplemented MC Scheme');
                    end
                    
                    
                    nextX = mcmcOut.nextX;
                    nextV = mcmcOut.nextV;
                    % one step forward induction end
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                end
                
                
                % at startDate, we reset strike
                if i==lastAliveExerciseIdx
                    comFwd = eqHeston.EQFwdMC(currentTime,nextX);
                    reSetS = comFwd;
                    
                end
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
           
           comFwd = eqHeston.EQFwdMC(currentTime,nextX);
           
           if strcmp(vanillaParams.params('callPutFlag'),'C')
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(comFwd(i)/reSetS(i) - relativeStrike*fwdRatio,0);
                    payoffStateB.cashflow(i) = max(comFwd(i)/reSetS(i) - relativeStrike*fwdRatio,0);
               end
           else
               for i=1:modelStatesSize
                    payoffStateA.cashflow(i) = max(-comFwd(i)/reSetS(i) + relativeStrike*fwdRatio,0);
                    payoffStateB.cashflow(i) = max(-comFwd(i)/reSetS(i) + relativeStrike*fwdRatio,0);
               end
           end
           
           payoffStateC.cashflow = comFwd;
           
%            df_ep = eqHeston.zeroCurve.DF(currentTime/365.0);
           
           df_ep = 1.0;
           
           % we don't discount forward price
           for i=1:modelStatesSize
                payoffStateA.cashflow_npv(i) = payoffStateA.cashflow(i)*df_ep;
                payoffStateB.cashflow_npv(i) = payoffStateB.cashflow(i)*df_ep;
                payoffStateC.cashflow_npv(i) =  payoffStateC.cashflow(i)*1.0;
           end
           
           
           %process payoff at maturity
            europeanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateA.cashflow;
            europeanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateA.cashflow_npv ;
            europeanValue.payoff = payoffStateA.cashflow_npv;
            
            americanValue.payoffStates.cashflow(:,currentNodeIdx) = payoffStateB.cashflow;
            americanValue.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateB.cashflow_npv ;
            americanValue.payoff = payoffStateB.cashflow_npv;
            
            nMFuture.payoffStates.cashflow(:,currentNodeIdx) = payoffStateC.cashflow;
            nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = payoffStateC.cashflow_npv ;
            nMFuture.payoff = payoffStateC.cashflow_npv;
            
           lastTimeIdx = currentTimeIdx;
           
%            Pricingidx = eqHeston.localVolSurface.Pricingidx;
           
           europeanValue.npv = mean(europeanValue.payoff);
           americanValue.npv = mean(americanValue.payoff);
           nMFuture.npv = mean(nMFuture.payoff);
            
           out.europeanValue = europeanValue; 
           out.americanValue = americanValue;
           out.nMFuture = nMFuture;
           
           out.fwdRatio = fwdRatio;
           
        end
        
        function out = CommoFwdNMMC(eqHeston,observeTime,modelStates)
            forwardCurve = eqHeston.forwardCurve.params('rawData');
            forwardCurveSize = size(forwardCurve,1);
            forwardMaturity = forwardCurve(:,1); 
            idx = find(observeTime <= forwardMaturity);
             if isempty(idx)
                idxNM = forwardCurveSize;
             else
                idxNM = min(idx);
             end
             
             %fwd(0,T_NM)
             fwd_NM = forwardCurve(idxNM,2);
             stateSize = length(modelStates);
             stochasticFwd = zeros(stateSize,1);
             
             for i=1:stateSize
                stochasticFwd(i) = fwd_NM * modelStates(i); 
             end
             
             out = stochasticFwd;
        end
        
        function columnOut = MCPayoffWorst(eqHeston,idx,comFwdWorst,currentTime, isStop,isKI,payoffInfo,columnIn)
            
            modelStatesSize = length(comFwdWorst);
            scheduleSize = payoffInfo.autoCallSchedule.scheduleSize;
            strike = payoffInfo.autoCallSchedule.strike(idx);
            coupon = payoffInfo.autoCallSchedule.coupon(idx);
            nominal = payoffInfo.nominal;
%             basePrice = payoffInfo.basePrice;
            lowerBarrier = payoffInfo.lowerBarrier;
            callStrike1 = payoffInfo.callStrike1;
            callValue1  = payoffInfo.callValue1;
            
            columnOut.isStop = zeros(modelStatesSize,scheduleSize);
            columnOut.worstP = zeros(modelStatesSize,scheduleSize);
            
            columnOut.isStop = columnIn.isStop;
            columnOut.worstP = columnIn.worstP;
            
            columnOut.payoffColumn.payoff = zeros(modelStatesSize,1);
            columnOut.payoffColumn.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
            columnOut.payoffColumn.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
            
            columnOut.payoffColumn = columnIn.payoffColumn;
            
            df_ep = eqHeston.zeroCurve.DF(currentTime/365.0);
            % early redemption
            % idx  : early redemption schedule iter
            % idx11: simulation path iter
            if idx == 1
                for idx11 =1:modelStatesSize % 1st early redemption
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                           columnOut.isStop(idx11,idx) = 1;
                           columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                           columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                           columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                           columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    
                end
                
            elseif idx > 1 && idx < scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv
                    else
                        % alive path
                        if comFwdWorst(idx11) >= strike % early redemption conditon met
                            columnOut.isStop(idx11,idx) = 1;
                            columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                            columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal*(1.0 + coupon);
                            columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = nominal*(1.0 + coupon)*df_ep;
                            columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                        end
                        
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                    end
                end
                
            else % idx == scheduleSize
                for idx11 =1:modelStatesSize
                    if columnOut.isStop(idx11,idx-1) == 1 % terminated path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = columnOut.worstP(idx11,idx-1);
                        columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx-1); %cached cashflow
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx-1); %cached cashflow_npv

                    else
                        %alive path
                        columnOut.isStop(idx11,idx) = 1;
                        columnOut.worstP(idx11,idx) = comFwdWorst(idx11);
                        % barrier hit path
                        if isKI(idx11) == 1
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        else % barrier unhit path
                            if comFwdWorst(idx11) < callStrike1 
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * callValue1/callStrike1* comFwdWorst(idx11);
                            elseif comFwdWorst(idx11) < strike
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon - callValue1)/(strike-callStrike1)*(comFwdWorst(idx11) - callStrike1) + nominal*callValue1; 
                            else
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                            
                            if comFwdWorst(idx11) > lowerBarrier
                                columnOut.payoffColumn.payoffStates.cashflow(idx11,idx) = nominal * (1.0 + coupon);
                            end
                        end
                        
                        % payoff postprocess
                        columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx) = columnOut.payoffColumn.payoffStates.cashflow(idx11,idx)*df_ep;
                        columnOut.payoffColumn.payoff(idx11) = columnOut.payoffColumn.payoffStates.cashflow_npv(idx11,idx);
                    end    
                end
            end    
            
            
        end
        
        function out = computeLocalVolGridHeston(eqHeston,timeGrid,strikeMoneynessGrid,smileDynamicsAdjFactors)
            % we look up implied volatility using smileDynamicsAdjFactors
            % applied  strikeMoneynessGrid

            % and when we calculate local vol using dupire formula we use
            % original strikeMoneynessGrid
            lookupMoneynessGrid = strikeMoneynessGrid * (1.0 + eqHeston.slope*(smileDynamicsAdjFactors - 1.0));
            localVolStrip = zeros(length(timeGrid),length(strikeMoneynessGrid));
            
            localVolC = zeros(length(timeGrid),length(strikeMoneynessGrid));
            localVolP = zeros(length(timeGrid),length(strikeMoneynessGrid));
            
            dt = 0.5*0.000001/365.0;
            ddt = 1.0/dt;
            dk = 0.01;
            ddk = 100.0;
            ddk2 = 10000.0;
            
            if timeGrid(1) == 0
                timeGrid(1) = 0.5*timeGrid(2);
            end
            timeGridR = timeGrid/365.0;
            
            

            for idxjj = 1:length(timeGrid)
                matT   = timeGridR(idxjj);
                f_matT = timeGridR(idxjj) + dt;
                b_matT = timeGridR(idxjj) - dt;
                for idxkk = 1:length(strikeMoneynessGrid)
                    f_strike_lookup =  lookupMoneynessGrid(idxkk) * exp(dk);
                    b_strike_lookup =  lookupMoneynessGrid(idxkk) * exp(-1.0*dk);
                    strike_lookup = lookupMoneynessGrid(idxkk);
                    logMoneyness = log(strikeMoneynessGrid(idxkk));
                    
                    heston_c = eqHeston.modelOTMPriceFwdMon(1.0,strike_lookup,matT*365.0,'Call');
                    f_heston_c = eqHeston.modelOTMPriceFwdMon(1.0,strike_lookup,f_matT*365.0,'Call');
                    b_heston_c = eqHeston.modelOTMPriceFwdMon(1.0,strike_lookup,b_matT*365.0,'Call');
                    f_k_heston_c = eqHeston.modelOTMPriceFwdMon(1.0,f_strike_lookup,matT*365.0,'Call');
                    b_k_heston_c = eqHeston.modelOTMPriceFwdMon(1.0,b_strike_lookup,matT*365.0,'Call');
 
                    d1_c = (f_heston_c - b_heston_c)*0.5*ddt;
                    d2_c = (f_k_heston_c - b_k_heston_c)*0.5*ddk;
                    d3_c = (f_k_heston_c - 2.0.*heston_c + b_k_heston_c)*ddk2;
                    
                    heston_p = eqHeston.modelOTMPriceFwdMon(1.0,strike_lookup,matT*365.0,'Put');
                    f_heston_p = eqHeston.modelOTMPriceFwdMon(1.0,strike_lookup,f_matT*365.0,'Put');
                    b_heston_p = eqHeston.modelOTMPriceFwdMon(1.0,strike_lookup,b_matT*365.0,'Put');
                    f_k_heston_p = eqHeston.modelOTMPriceFwdMon(1.0,f_strike_lookup,matT*365.0,'Put');
                    b_k_heston_p = eqHeston.modelOTMPriceFwdMon(1.0,b_strike_lookup,matT*365.0,'Put');
                    
                    d1_p = (f_heston_p - b_heston_p)*0.5*ddt;
                    d2_p = (f_k_heston_p - b_k_heston_p)*0.5*ddk;
                    d3_p = (f_k_heston_p - 2.0.*heston_p + b_k_heston_p)*ddk2;

                    localVolC(idxjj,idxkk) = d1_c/(0.5*(d3_c - d2_c));
                    localVolP(idxjj,idxkk) = d1_p/(0.5*(d3_p - d2_p));
                    if strikeMoneynessGrid(idxkk) <= 1.0
                        localVolStrip(idxjj,idxkk) = localVolP(idxjj,idxkk); 
                    else
                        localVolStrip(idxjj,idxkk) = localVolC(idxjj,idxkk); 
                    end
      
                end
            end
            
            % if vol is wrong then do the flat extrapol in time direction
            for idxjj = length(timeGrid)-1:-1:1
                volTimeSlice =localVolStrip(idxjj,:);
                
                if max(volTimeSlice) >= 5.0 || min(volTimeSlice) <= 0.0
                    localVolStrip(idxjj,:) = localVolStrip(idxjj+1,:);
                end
            end
%             localVolStrip = volTimeSlice;
            
            out.localVolStrip = localVolStrip;
            out.localVolC = localVolC;
            out.localVolP = localVolP;
        end
        
        function out = computeLocalVolGridSSSABR(eqHeston,timeGrid,strikeMoneynessGrid,smileDynamicsAdjFactors)
            % we look up implied volatility using smileDynamicsAdjFactors
            % applied  strikeMoneynessGrid

            % and when we calculate local vol using dupire formula we use
            % original strikeMoneynessGrid
            lookupMoneynessGrid = strikeMoneynessGrid * (1.0 + eqHeston.slope*(smileDynamicsAdjFactors - 1.0));
            localVolStrip = zeros(length(timeGrid),length(strikeMoneynessGrid));
            
            dt = 0.5*0.000001/365.0;
            ddt = 1.0/dt;
            dk = 0.01;
            ddk = 100.0;
            ddk2 = 10000.0;
            
            if timeGrid(1) == 0
                timeGrid(1) = 0.5*timeGrid(2);
            end
            timeGridR = timeGrid/365.0;
            

            for idxjj = 1:length(timeGrid)
                matT   = timeGridR(idxjj);
                f_matT = timeGridR(idxjj) + dt;
                b_matT = timeGridR(idxjj) - dt;
                for idxkk = 1:length(strikeMoneynessGrid)
                    f_strike_lookup =  lookupMoneynessGrid(idxkk) * exp(dk);
                    b_strike_lookup =  lookupMoneynessGrid(idxkk) * exp(-1.0*dk);
                    strike_lookup = lookupMoneynessGrid(idxkk);
                    logMoneyness = log(strikeMoneynessGrid(idxkk));
                    
                    sabr_imv = eqHeston.Heston_ImpVol(strike_lookup,matT);
                    total_var = sabr_imv * sabr_imv * timeGridR(idxjj);
                    f_sabr_imv = eqHeston.Heston_ImpVol(strike_lookup,f_matT);
                    b_sabr_imv = eqHeston.Heston_ImpVol(strike_lookup,b_matT);
                    f_total_var = f_sabr_imv * f_sabr_imv * f_matT;
                    b_total_var = b_sabr_imv * b_sabr_imv * b_matT;
                    d1 = (f_total_var - b_total_var)*0.5*ddt;

                    f_k_sabr_imv = eqHeston.Heston_ImpVol(f_strike_lookup,matT);
                    b_k_sabr_imv = eqHeston.Heston_ImpVol(b_strike_lookup,matT);
 
                    f_k_total_var = f_k_sabr_imv * f_k_sabr_imv * matT;
                    b_k_total_var = b_k_sabr_imv * b_k_sabr_imv * matT;

                    d2 = (f_k_total_var - b_k_total_var)*0.5*ddk;
                    d3 = (f_k_total_var - 2.0.*total_var + b_k_total_var)*ddk2;

                    localVolStrip(idxjj,idxkk) = d1/(1 - logMoneyness/total_var*d2 + 0.25*(-0.25 - 1/total_var + logMoneyness*logMoneyness/(total_var*total_var))*d2*d2 + 0.5*d3);
      
                end
            end
            
            out = localVolStrip;
        end
        
        function localVol = InterpolateLocalVolSSSABR(eqHeston,x,fromTime)

            expiry = eqHeston.localVolSurface.localVolStripExpiry;
            
            %find which strip fromTime belongs to 
            idxS = find(expiry > fromTime);
            if isempty(idxS)
                idxStrip = length(expiry);
            else
                idxStrip = min(idxS);
            end
            
            % find exact timeSlice in the given strip
            localVolTimeStep = eqHeston.localVolSurface.localVolTimeStep{idxS};
            localVolSurfaceSABR = eqHeston.localVolSurface.localVolSurfaceSABR{idxS};
            forwardMoneyness = eqHeston.localVolSurface.forwardMoneyness{idxS};

            idx = find(localVolTimeStep > fromTime);
            if isempty(idx)
                idxNow = length(localVolTimeStep);
            else
                idxNow = min(idx);
            end
            
            localVolLine = localVolSurfaceSABR(idxNow,:);
%             forwardMoneynessLine = forwardMoneyness(idxNow,:);
            
            localVol =  zeros(length(x),1);
            for ii =1:length(x)
                dummyVariance = H_interpolation(forwardMoneyness,localVolLine,x(ii),1);
                localVol(ii) = sqrt(dummyVariance);
            end

        end
        
        function mcmcOut = inductMCForwardNewSSSABR(eqHeston,fromTime,toTime,lastX,dZ)
            
            predictor = lastX;
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime);
            %lookup issue add small epsilon to fromTime
%             localVol = eqCOMDupireSpotGF.InterpolateLocalVol(predictor,fromTime + 0.01);
            lookupTime = max(fromTime-0.01,0);
            localVol = eqHeston.InterpolateLocalVolSSSABR(predictor,lookupTime);
            
            Dt = (toTime - fromTime)/365.0;
            sqrtDt = sqrt(Dt);
            for i=1:length(lastX)
%                 predictor(i) = predictor(i)*(1 + localVol(i)*sqrtDt*dZ(i)); 
                predictor(i) = predictor(i)*exp(-0.5*localVol(i)*localVol(i)*Dt + localVol(i)*sqrtDt*dZ(i)); 
                
            end
            
            mcmcOut.nextX = predictor;
            
        end
        
        function out = computeStepdown1SMCReducedInt(eqHeston,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqHeston.localVolSurface.expiry;
            
            volExpiryAlive = expiry(find(expiry <= maturity));
            
            if expiry(end) <= maturity
                localVolStripSize = length(volExpiryAlive);
                localVolStripExpiry = expiry;
            else
                localVolStripSize = length(volExpiryAlive) + 1;
                localVolStripExpiry = [volExpiryAlive;maturity];
            end

%             volExpiryAliveSize = length(volExpiryAlive);
            % we include valueDate in the scheduel
            volExpiry =[volExpiryAlive;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqHeston.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% local vol surface construct from parmetric implied vol surface start
            localVolSurfaceSABR = cell(localVolStripSize,1);
            forwardMoneyness = cell(localVolStripSize,1);
            localVolTimeStep = cell(localVolStripSize,1);
            
            settleFutures    = eqHeston.settleFutures;
            settleFuturesRef = eqHeston.settleFuturesRef;
            atmVols          = eqHeston.atmVols;
            

            smileDynamicsAdjFactors = zeros(localVolStripSize,1);
            dy = 0.05;
            for idxhh=1:localVolStripSize
                
                timeStepStrip1 = timeStep(find(timeStep <= localVolStripExpiry(idxhh)));
                if idxhh > 1
                    timeStepStrip = timeStepStrip1(find(timeStepStrip1 > localVolStripExpiry(idxhh-1)));
                else
                    timeStepStrip = timeStepStrip1;
                end
                
                timeStepStrip = sort(timeStepStrip,'ascend');
                localVolTimeStep{idxhh} = timeStepStrip;
                
                x_max = max(1.3,settleFuturesRef(idxhh)/settleFutures(idxhh)*exp( 3.0*atmVols(idxhh)*sqrt(localVolStripExpiry(idxhh)/365.0)));
                x_min = min(0.7,settleFuturesRef(idxhh)/settleFutures(idxhh)*exp(-3.0*atmVols(idxhh)*sqrt(localVolStripExpiry(idxhh)/365.0)));

                smileDynamicsAdjFactors(idxhh) = settleFutures(idxhh)/settleFuturesRef(idxhh);

                gridSize = floor(log(x_max/x_min)/dy) + 1;
                localVolStrip= zeros(length(timeStepStrip),gridSize);
                forwardMoneynessStrip = zeros(1,gridSize);
                
                for idxjj=1:gridSize
                    forwardMoneynessStrip(idxjj) = x_min*exp((idxjj-1)*dy);
                end
                forwardMoneyness{idxhh} = forwardMoneynessStrip;
                
%                 localVolStrip = eqHeston.computeLocalVolGridSSSABR(timeStepStrip,forwardMoneynessStrip,smileDynamicsAdjFactors(idxhh));
                dummyOuthh = eqHeston.computeLocalVolGridHeston(timeStepStrip,forwardMoneynessStrip,smileDynamicsAdjFactors(idxhh));
                localVolStrip = dummyOuthh.localVolStrip;
                
                localVolSurfaceSABR{idxhh} = localVolStrip;
            end

            eqHeston.localVolSurface.localVolSurfaceSABR = localVolSurfaceSABR;
            eqHeston.localVolSurface.forwardMoneyness = forwardMoneyness;
            eqHeston.localVolSurface.localVolTimeStep = localVolTimeStep;
            eqHeston.localVolSurface.localVolStripExpiry = localVolStripExpiry;

          %% local vol surface construct from parmetric implied vol surface end
          
          %% MCMC init 
            useQuasiRandomYN = eqHeston.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
%                 NMC = 2^14;
%                 NMC = 2^16;
                NMC = eqHeston.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                Ps = sobolset(MCTimeStep,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqHeston.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end
%                U = dZ;
            else
                rng('default');
                rng(0);
                
                NMC = eqHeston.modelParams('NMC'); 
%                 NMC = 50000;
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
%                 Z= randn(NMC/2,MCTimeStep);
                Z= randn(NMC/2,MCTimeStep);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           initX = ones(NMC,1);
%            Pricingidx = eqCOMDupireSpotGF.localVolSurface.Pricingidx;
%            initXIdx = ones(NMC,1)*Pricingidx;
           
           nextX = initX;
%            nextXIdx = initXIdx;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMMCReduced(currentTime,nextX);
           comFwd = eqHeston.CommoFwdNMMC(currentTime,nextX);
           
           isKI = eqHeston.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
%                 Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
%                     mcmcOut   = inductMCForwardNew(eqCOMDupireSpotGF,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
                    mcmcOut   = inductMCForwardNewSSSABR(eqHeston,timeStep(idx),timeStep(idx+1),nextX,U(:,idx));
              
                    nextX = mcmcOut.nextX;
%                     nextXIdx = mcmcOut.nextXIdx;
                    % one step backward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
%                     comFwd = eqCOMDupireSpotGF.CommoFwdNMMCReduced(currentTime,nextX);
                    comFwd = eqHeston.CommoFwdNMMC(currentTime,nextX);
                    
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqHeston,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
%                 dummyisKI = ones(modelStatesSize,1);
%                 columnout   = MCPayoff(eqCOMDupireSpotGF,i,comFwd,currentTime,isStop,dummyisKI,payoffInfo,columnIn);
%                 
%                 columnOut = eqCOMDupireSpotGF.MCPayoff(i,comFwd,currentTime,isStop,isKI,payoffInfo,columnIn);
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqHeston.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqHeston.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function out = computeStepdown1SMC(eqHeston,valueDate,stepdownParams)
%             out =0;
            % model schedule generation
            scheduleInt = stepdownParams.params('autoCallScheduleInt');
            scheduleSize = size(scheduleInt,1);
            autoCallSchedule=[];
            for i=1:scheduleSize
                autoCallSchedule.exerciseDate(i) = H_Date(scheduleInt(i,1));
                autoCallSchedule.days(i) = DateDiff(autoCallSchedule.exerciseDate(i),valueDate);
                autoCallSchedule.strike(i) = scheduleInt(i,2);
                autoCallSchedule.coupon(i) = scheduleInt(i,3);
            end
            autoCallSchedule.scheduleSize = scheduleSize;
            
            expiryDate = autoCallSchedule.exerciseDate(scheduleSize);
            
            % if valueDate is passed expiryDate then price is 0
            maturity = DateDiff(expiryDate,valueDate);
            if maturity <=0
                out = 0;
                return;
            end
            
            expiredChance = 0;
            aliveChance = 0;
            expiry = eqHeston.localVolSurface.expiry;
            volExpiry = expiry(find(expiry <= maturity));
            % we include valueDate in the scheduel
            volExpiry =[volExpiry;0];
            
            timeStep = volExpiry;
            if strcmp(stepdownParams.params('dailyTimeStepsYN'),'YES')
                dailyTimeSteps = [maturity:-1:0]';
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            else
                timeStepP = eqHeston.modelParams('mcOneTimeStep');
                dailyTimeSteps = [maturity:-timeStepP:0]';
                dailyTimeSteps = [dailyTimeSteps;0];
                timeStep = sort(union(timeStep,dailyTimeSteps),'ascend');
            end
            
            % we include exerciseDates
            for i= 1:scheduleSize
                daysToExercise = autoCallSchedule.days(i);
                if daysToExercise <= 0
                    expiredChance = expiredChance +1;
                    continue;
                else
                    aliveChance = aliveChance + 1;
                    timeStep = [timeStep; daysToExercise];
                end 
            end
            lastAliveExeriseIdx = 1 + expiredChance;
            
            
            timeStep = sort(union(timeStep,maturity),'ascend');
            totalTimeStepSize = length(timeStep);
            eventTimeIdx = zeros(scheduleSize,1);
            
            for i= scheduleSize:-1:lastAliveExeriseIdx
                idx = find(timeStep == autoCallSchedule.days(i));
                eventTimeIdx(i) = min(idx);
            end
           
          %% MCMC init 
            useQuasiRandomYN = eqHeston.modelParams('useQuasiRandomYN');
%             useQuasiRandomYN = 'true';
            
            if strcmp(useQuasiRandomYN,'true')
                NMC = eqHeston.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                numOfFactors = 2;
                Ps = sobolset(MCTimeStep*numOfFactors,'Skip',NMC);
                Q = qrandstream(Ps);

                reset(Q);
                U0 = qrand(Q,NMC);
                U = zeros(NMC,MCTimeStep*numOfFactors);

                dZ0 = zeros(size(U,1),size(U,2));
    %             dZ = norminv(U);
                % Use Accurate Normal Inverse Method , ASA241 by Michael Wichura
                % generate random number from the end
                for i=1:size(U,1)
                    for j=1:size(U,2)
                        dZ0(i,j) = r8_normal_01_cdf_inverse(U0(i,j));
                    end
                end
            
               % apply brownian bridge
               dZ = eqHeston.bbgenerator(dZ0);
               U(:,1) = dZ(:,1);
               for i=2:size(dZ,2)
                   U(:,i) = dZ(:,i) - dZ(:,i-1); 
               end

            else
                rng('default');
                rng(0);
                
                NMC = eqHeston.modelParams('NMC'); 
                MCTimeStep = totalTimeStepSize -1; % nowDate (0) should be skipped
                numOfFactors = 2;
                Z= randn(NMC/2,MCTimeStep*numOfFactors);
                Z=[Z;-Z];
                Z=Z';
                
                %TimeInversion
                sizeZ = size(Z,1);
                A = zeros(sizeZ,sizeZ);
                for i=1:sizeZ
                    A(i,sizeZ + 1 -i) = 1;
                end
                Z = A*Z;
                
                U = Z';

            end
            
           currentTime = 0; %NowDate
           currentTimeIdx = 1; % 1st Time Steps
           currentNodeIdx = 1; % no eventDate for nowDate
           lastTimeIdx = currentTimeIdx;
           
           % initial modelState
           %  X  = S(t)/F(0,t)  : spot process
           %  V  = instantaneous variance proces
           
           initX = ones(NMC,1);
           initV = ones(NMC,1)*eqHeston.v0;
           
           nextX = initX;
           nextV = initV;
            
          %% payoff init
           nominal = stepdownParams.params('nominal');
           basePrice = stepdownParams.params('basePrice');
           lowerBarrier = stepdownParams.params('lowerBarrier');
           overHedgeShift = stepdownParams.params('overHedgeShift');
           overHedgeSpread = stepdownParams.params('overHedgeSpread');
           
           callStrike1 = stepdownParams.params('callStrike1');
           callValue1 = stepdownParams.params('callValue1');
           SSpayoffYN = stepdownParams.params('SSpayoffYN');
           KIYN = stepdownParams.params('KIYN');
           
           payoffInfo.nominal = nominal;
           payoffInfo.basePrice = basePrice;
           payoffInfo.lowerBarrier = lowerBarrier;
           payoffInfo.overHedgeShift = overHedgeShift;
           payoffInfo.overHedgeSpread = overHedgeSpread;
           
           payoffInfo.callStrike1 = callStrike1;
           payoffInfo.callValue1 = callValue1;
           payoffInfo.SSpayoffYN = SSpayoffYN;
           
           payoffInfo.autoCallSchedule = autoCallSchedule;
           
           
           modelStatesSize = NMC;
           %down barrier already touch
           hitValue.npv = 0;
           hitValue.payoff = zeros(modelStatesSize,1);
           hitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           hitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % down barrier no touch
           unhitValue.npv = 0;
           unhitValue.payoff = zeros(modelStatesSize,1);
           unhitValue.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           unhitValue.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % dummy nearest month future price
           nMFuture.npv = 0;
           nMFuture.payoff = zeros(modelStatesSize,1);
           nMFuture.payoffStates.cashflow = zeros(modelStatesSize,scheduleSize);
           nMFuture.payoffStates.cashflow_npv = zeros(modelStatesSize,scheduleSize);
           
           % intermediate variables
           payoffStateA.cashflow = zeros(modelStatesSize,1);
           payoffStateA.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateB.cashflow = zeros(modelStatesSize,1);
           payoffStateB.cashflow_npv = zeros(modelStatesSize,1);
           
           payoffStateC.cashflow = zeros(modelStatesSize,1);
           payoffStateC.cashflow_npv = zeros(modelStatesSize,1);
           
           % variable to use for early redemption check and barrier check 
           isStop = zeros(modelStatesSize,scheduleSize);
           worstP = zeros(modelStatesSize,scheduleSize);
           
           if KIYN == true
               isKI = ones(modelStatesSize,1);
           else
               isKI = zeros(modelStatesSize,1);
           end
           
           % check whether current future price breach the barrier
           comFwd = eqHeston.EQFwdMC(currentTime,nextX);
%            comFwd = eqCOMDupireSpotGF.CommoFwdNMMC(currentTime,nextX);
           isKI = eqHeston.BarrierCheck(comFwd,isKI,payoffInfo);
%           BarrierCheck(eqCOMDupireSpotGF,comFwd,isKI,payoffInfo)
           %% Path Generation Forward
           for i=lastAliveExeriseIdx:1:scheduleSize
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i-1);
                    endTimeIdx = eventTimeIdx(i);
                else
                    startTimeIdx = 1; % valueDate
                    endTimeIdx = eventTimeIdx(i);  
                end
                
                endTimeIdx = endTimeIdx - 1;
                
            %% induction Forward start
%                 Ks = eqCOMDupireSpotGF.localVolSurface.Ks;
                for idx= startTimeIdx:1:endTimeIdx
                    if strcmp(eqHeston.modelParams('MCScheme'), 'QE')
                        mcmcOut   = inductMCForwardQE(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    elseif strcmp(eqHeston.modelParams('MCScheme'), 'NonCentralChiSquare')
                        mcmcOut   = inductMCForwardNCCS(eqHeston,timeStep(idx),timeStep(idx+1),nextX,nextV,U(:,2*(idx-1)+1),U(:,2*(idx-1)+2));
                    end
                    nextX = mcmcOut.nextX;
                    nextV = mcmcOut.nextV;
                    % one step forward induction end
                    % barrier check
                    lastTimeIdx = lastTimeIdx + 1;
                    currentTime = timeStep(lastTimeIdx);
                    comFwd = eqHeston.EQFwdMC(currentTime,nextX);
                    % per each path check whether Barrier was breached 
                    isKI = BarrierCheck(eqHeston,comFwd,isKI,payoffInfo);
                end
                
                
                %forward payoff handling
                columnIn.isStop = isStop;
                columnIn.worstP = worstP;
                columnIn.payoffColumn = unhitValue;
                comFwdWorst = comFwd/payoffInfo.basePrice; 
                columnOut = eqHeston.MCPayoffWorst(i,comFwdWorst,currentTime,isStop,isKI,payoffInfo,columnIn);
                isStop = columnOut.isStop;
                worstP = columnOut.worstP;
                unhitValue = columnOut.payoffColumn;
                
                
                nMFuture.payoffStates.cashflow(:,currentNodeIdx) = comFwd;
                nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx) = comFwd ;
                nMFuture.payoff = comFwd;
                
                %induct forward for eventDate
                currentNodeIdx = currentNodeIdx + 1;
           end
          
%            lastTimeIdx = currentTimeIdx;
          %% Forward Induction End
            
          %% Backward Induction Start (Regression)
           for i=scheduleSize:-1:lastAliveExeriseIdx
                % past schedule neglect
                if DateDiff(valueDate,autoCallSchedule.exerciseDate(i)) >= 0, continue;end
                if i > lastAliveExeriseIdx
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = eventTimeIdx(i-1);
                else
                    startTimeIdx = eventTimeIdx(i);
                    endTimeIdx = 1;  % valueDate
                end
%                 endTimeIdx = endTimeIdx + 1;
                currentTime = timeStep(endTimeIdx);
                
                %induct backward for eventDate
                currentNodeIdx = currentNodeIdx - 1;
                nMFuture.payoff = nMFuture.payoffStates.cashflow_npv(:,currentNodeIdx);
              %% AtDate operation on Early ExerciseDate
                if i > lastAliveExeriseIdx
                    strikeEarly = autoCallSchedule.strike(i-1);
                    couponEarly = autoCallSchedule.coupon(i-1);
                    
                    exerciseValue = zeros(modelStatesSize,1);
                    contiValue = zeros(modelStatesSize,1);
                    
%                     onePayoffD = ones(modelStatesSize,1);
                    onePayoffD = eqHeston.zeroCurve.DF(currentTime/365.0);
                    
                    % we only use paths that is still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 
                            contiValue(idx) = unhitValue.payoff(idx)/onePayoffD;
                        else
                            contiValue(idx) = unhitValue.payoff(idx);
                        end
                    end
                    
%                     contiValue = unhitValue.payoffStates.cashflow(:,i-1);
                    contiValue = contiValue/10000;
                    
                    decisionVar1 = worstP(:,i-1);
                    % we use upto 2nd order polynomial as regression
                    % equatioin
                    dimensionLS = 4;
                    regMatrix = ones(modelStatesSize,dimensionLS);
                    for idx_r=1:modelStatesSize
                        regMatrix(idx_r,2) = decisionVar1(idx_r);
                        regMatrix(idx_r,3) = decisionVar1(idx_r)*decisionVar1(idx_r);
                        regMatrix(idx_r,4) = decisionVar1(idx_r)*decisionVar1(idx_r)*decisionVar1(idx_r);
                    end
                    % we use only alive path at the execise date as
                    % regression input
                    beta =zeros(dimensionLS,1);
                    
                    numSim = 0;
                    regMatrix2 = zeros(dimensionLS,dimensionLS);
                    contiValue2 = zeros(dimensionLS,1);
%                     aliveMatrix = zeros(modelStatesSize,modelStatesSize);
                    aliveVector = zeros(modelStatesSize,1);
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0 % alive path at the start of the period (early exercise date
                            numSim = numSim +1;
%                             aliveMatrix(idx,idx) = 1;
                            aliveVector(idx) = 1;
                            
                            if worstP(idx,i-1) < strikeEarly - couponEarly/overHedgeSpread
                                exerciseValue(idx) = contiValue(idx);
                            elseif worstP(idx,i-1) < strikeEarly
                                exerciseValue(idx) = (1.0 + couponEarly + (worstP(idx,i-1) - strikeEarly)*overHedgeSpread);
                            end
                        else % for terminated path we do nothing
                            exerciseValue(idx) = contiValue(idx);
%                             exerciseValue(idx) = unhitValue.payoffStates.cashflow(idx,i-1)/10000;
                        end
                        
                    end
                    
                    % if we have live paths, then we do the regression
                    if numSim > 0
%                         regMatrix2 =  regMatrix' * aliveMatrix * regMatrix;
%                         contiValue2 = regMatrix' * aliveMatrix * contiValue;
                        regMatrix2 = zeros(dimensionLS,dimensionLS);
                        contiValue2 = zeros(dimensionLS,1);
                        for ii=1:dimensionLS
                            regVi = regMatrix(:,ii);
                            for jj=1:dimensionLS
                                regVj = regMatrix(:,jj);
                                for idx3=1:modelStatesSize
                                    regMatrix2(ii,jj) = regMatrix2(ii,jj) + regVi(idx3)*aliveVector(idx3)*regVj(idx3);
                                end
                            end
                            for idx3=1:modelStatesSize
                                contiValue2(ii) = contiValue2(ii) + regVi(idx3)*aliveVector(idx3)*contiValue(idx3);
                            end
                        end
                        
                        beta = regress(contiValue2,regMatrix2);
                        regContiValue = regMatrix*beta;
                        
                        for idx=1:modelStatesSize
                            if isStop(idx,i-1) == 0 %live path
                                % regContiValue is only used for decision making
                                if regContiValue(idx) <= exerciseValue(idx) 
                                    contiValue(idx) = exerciseValue(idx);
                                end
                            else  % terminated path we do nothing
                                contiValue(idx) = exerciseValue(idx);
                            end
                        end
                    else % there is no alive path then we do nothing
                        for idx=1:modelStatesSize
                            contiValue(idx) = exerciseValue(idx);
                        end
                    end
                    
                    % we only apply regression to those paths that are still alive for regression
                    for idx=1:modelStatesSize
                        if isStop(idx,i-1) == 0  % live path
                            unhitValue.payoff(idx) = contiValue(idx)*onePayoffD;
                        else
                            unhitValue.payoff(idx) = contiValue(idx);
                        end
                    end
                    
                    unhitValue.payoff = unhitValue.payoff * 10000;
                    
                    
                end
                % we are at the start of the period
                
            end

%            hitValue.npv = hitValue.payoff(Pricingidx);
           unhitValue.npv = mean(unhitValue.payoff);
           nMFuture.npv =   mean(nMFuture.payoff);
%            nMFuture.npv = nMFuture.payoff(Pricingidx);
           
%            out.hitValue = hitValue; 
           out.unhitValue = unhitValue;
           out.nMFuture = nMFuture; 
        end
        
        function  output  = TargetFunctionHestonGlobalGA(eqHeston,tvar,optParams)
    
            model_otmPrice = 0.0;
            market_otmPrice = 0.0;

            % assigning model parameters
            eqHeston.kappa = tvar(1);
            eqHeston.theta = tvar(2);
            eqHeston.rho = tvar(3);
            eqHeston.sigma = tvar(4);
            eqHeston.v0 = tvar(5);

            % cost function for levenberg marquardt algorithm
            out= zeros(optParams.numOfEquation,1);
            idx =1;

            expiry = optParams.params.expiry;
            strike = optParams.params.strike;
            spot =  eqHeston.spot.params('rawData');

           if  strcmp(optParams.params.calibrationErrorType,'impVolError')
               for i=1:optParams.params.expirySize
                   fwd = eqHeston.Fwd(spot,expiry(i));
                    for j=1:optParams.params.strikeSize
                        if optParams.params.calibrationYN(i,j) == 1
                            market_vol = optParams.params.blackVol(i,j);
                            marketStrike = optParams.params.marketStrikes(i,j);
                            model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                            model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                            out(idx) = model_vol - market_vol;
                            idx = idx + 1;
                        end
                    end
               end
           elseif strcmp(optParams.params.calibrationErrorType,'priceError')
               for i=1:optParams.params.expirySize
                   fwd = eqHeston.Fwd(spot,expiry(i));
                    for j=1:optParams.params.strikeSize
                        if optParams.params.calibrationYN(i,j) == 1
                            market_otmPrice = optParams.params.blackOTMPrice(i,j);
                            marketStrike = optParams.params.marketStrikes(i,j);
                            model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                            out(idx) = model_otmPrice - market_otmPrice;
                            idx = idx + 1;
                        end
                    end
               end
           elseif strcmp(optParams.params.calibrationErrorType,'relativePriceErrorSS')
               for i=1:optParams.params.expirySize
                   fwd = eqHeston.Fwd(spot,expiry(i));
                    for j=1:optParams.params.strikeSize
                        if optParams.params.calibrationYN(i,j) == 1
                            market_otmPrice = optParams.params.blackOTMPrice(i,j);
                            marketStrike = optParams.params.marketStrikes(i,j);
                            model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                            out(idx) = (model_otmPrice/market_otmPrice - 1.0)*sqrt(expiry(i)/365.0);
                            idx = idx + 1;
                        end
                    end
                end
           elseif strcmp(optParams.params.calibrationErrorType,'relativePriceError')
               for i=1:optParams.params.expirySize
                   fwd = eqHeston.Fwd(spot,expiry(i));
                    for j=1:optParams.params.strikeSize
                        if optParams.params.calibrationYN(i,j) == 1
                            market_otmPrice = optParams.params.blackOTMPrice(i,j);
                            marketStrike = optParams.params.marketStrikes(i,j);
                            model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                            out(idx) = model_otmPrice/market_otmPrice - 1.0;
                            idx = idx + 1;
                        end
                    end
               end
           else
               error('unknown calibrationErrorType!')
           end

           output = 0.0;
           dummyN = 0;
           for i=1:length(out)
               output = output + out(i)*out(i);
               dummyN = dummyN + 1;
           end

           output = output/dummyN;
        end
        
        function output = BoundaryConditionCheck(eqHeston,popt,lb,ub)
            output = true;
            
            if length(popt) ~= length(lb) || length(popt) ~= length(ub)
                output = false;
            end
            
            for i=1:length(popt)
                if popt(i) < lb(i) || popt(i) > ub(i)
                    output = false;
                    break;
                end
            end
            
        end
        
        function out = CalibrateToVolSurface(eqHeston,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrice = zeros(expirySize,strikeSize);
            blackOTMPrice2 = zeros(expirySize,strikeSize);
            blackOTMVega = zeros(expirySize,strikeSize);
            fwdMoneyness = zeros(expirySize,strikeSize);
            marketStrikes = zeros(expirySize,strikeSize);
            
            calibrationYN = zeros(expirySize,strikeSize);
            
            strikeBoundExpiry = eqHeston.strikeUseBound(:,1);
%             lowerStrikeBound = eqHeston.strikeUseBound(:,2);
%             upperStrikeBound = eqHeston.strikeUseBound(:,3);
            
            % undiscounted OTM(call for k>1
            if strcmp(volSurface.params('moneyNessType'),'fwdMoneyNess') || strcmp(volSurface.params('moneyNessType'),'fwdMoneyNessSSR')
                for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
                    fwd = 1.0;
                    
                    idxDummy = find(expiry(k)<=strikeBoundExpiry);
                    if ~isempty(idxDummy)
                        idxDummy2 = min(idxDummy);
                        lowerStrikeBound = eqHeston.strikeUseBound(idxDummy2,2);
                        upperStrikeBound = eqHeston.strikeUseBound(idxDummy2,3);
            
                    else
                        lowerStrikeBound = eqHeston.strikeUseBound(end,2);
                        upperStrikeBound = eqHeston.strikeUseBound(end,3);
                    end
    %                 df = black.zeroCurve.DF(expiry(k)/365.0);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j);
                        marketStrikes(k,j) = fwd*strike(j);
                        % multiplied by fwd
                        if fwdMoneyness(k,j) >= lowerStrikeBound && fwdMoneyness(k,j) <= upperStrikeBound
                            calibrationYN(k,j) = 1;
                        end
                        
%                         calibrationYN(k,j) = 1;
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                    end
                end
            elseif strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
                for k=1:expirySize
                    fwd = black.Fwd(spot,expiry(k));
                    idxDummy = find(expiry(k)<=strikeBoundExpiry);
                    if ~isempty(idxDummy)
                        idxDummy2 = min(idxDummy);
                        lowerStrikeBound = eqHeston.strikeUseBound(idxDummy2,2);
                        upperStrikeBound = eqHeston.strikeUseBound(idxDummy2,3);
            
                    else
                        lowerStrikeBound = eqHeston.strikeUseBound(end,2);
                        upperStrikeBound = eqHeston.strikeUseBound(end,3);
                    end
                    
                    fwdFactor = eqHeston.FwdFactor(expiry(k));
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdStrike = strike(j)/fwdFactor;
                        fwdMoneyness(k,j) = fwdStrike;
                        marketStrikes(k,j) = fwd*fwdMoneyness(k,j);
                        % multiplied by fwd
                        % test
                        calibrationYN(k,j) = 1;
%                         if fwdMoneyness(k,j) >= lowerStrikeBound && fwdMoneyness(k,j) <= upperStrikeBound
%                             calibrationYN(k,j) = 1;
%                         end
                        
                        if fwdStrike <= 1.0
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                    end
                end
            else
                for k=1:expirySize
                    fwd = black.Fwd(spot,expiry(k));
                    idxDummy = find(expiry(k)<=strikeBoundExpiry);
                    if ~isempty(idxDummy)
                        idxDummy2 = min(idxDummy);
                        lowerStrikeBound = eqHeston.strikeUseBound(idxDummy2,2);
                        upperStrikeBound = eqHeston.strikeUseBound(idxDummy2,3);
            
                    else
                        lowerStrikeBound = eqHeston.strikeUseBound(end,2);
                        upperStrikeBound = eqHeston.strikeUseBound(end,3);
                    end
    %                 df = black.zeroCurve.DF(expiry(k)/365.0);
                    for j=1:strikeSize
                        blackVol(k,j) = volSurface.volSurfaceR(k,j);
                        fwdMoneyness(k,j) = strike(j);
                        marketStrikes(k,j) = fwd*strike(j);
                        % multiplied by fwd
%                         if fwdMoneyness(k,j) >= lowerStrikeBound && fwdMoneyness(k,j) <= upperStrikeBound
%                             calibrationYN(k,j) = 1;
%                         end
                        
                        calibrationYN(k,j) = 1;
                        
                        if fwdMoneyness(k,j) <= 1
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                        else
                            blackOTMPrices(k,j) = fwd*black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                        end
                        
                    end
                end
            end
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            params.blackVol = blackVol;
            params.fwdMoneyNess = fwdMoneyness;
            params.marketStrikes = marketStrikes;
            params.calibrationYN = calibrationYN;
            
            eqHeston.fwdMoneyNess = fwdMoneyness;
            
            params.blackOTMPrice = blackOTMPrices;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            params.kappa = eqHeston.kappa;
            params.theta = eqHeston.theta;
            params.rho = eqHeston.rho;
            params.sigma = eqHeston.sigma;
            params.v0 = eqHeston.v0;
            
            params.calibrationErrorType = eqHeston.calibrationErrorType;
            %output vol proxy
            out.marketStrikes = params.fwdMoneyNess;
            out.fwdMoneyNess = params.fwdMoneyNess;
            out.expiry = params.expiry;
            out.strike = params.strike;
            
            out.blackOTMPrice = blackOTMPrices;
            out.hestonOTMPrice = zeros(expirySize,strikeSize);
            out.hestonBlackVol = zeros(expirySize,strikeSize);
            out.re = zeros(expirySize,strikeSize);
            out.voldiff = zeros(expirySize,strikeSize);
            out.rmseTotal=0.0;
            out.volmseTotal = 0.0;
            
            
            calibrationType = 'global';
            if nargin < 3
                calibrationType = 'global'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'global'
                    
                    optParams.params = params;
                    optParams.modelParamsSize = 5;  % kappa, theta, rho, sigma, v0,
                    optParams.numOfEquation = params.expirySize*params.strikeSize + ...  % target opm options
                                              0;   % constraint
                    
                    tvar = zeros(optParams.modelParamsSize,1);
                    
                    tvar(1) = eqHeston.kappa;
                    tvar(2) = eqHeston.theta;
                    tvar(3) = eqHeston.rho;
                    tvar(4) = eqHeston.sigma;
                    tvar(5) = eqHeston.v0;
                    
                    % initial parameters costval
%                     options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
                    options=[1E-03, 1E-25, 1E-25, 1E-25, 1E-25];
                    x=  zeros(optParams.numOfEquation,1);
                    lb = [0.0001,0.0001,-0.9999,0.0001,0.0001];
                    ub = [100.0,100.0,0.9999,100.0,100.0];
                    tic
                    [ret, popt, info, covar]=levmar('TargetFunctionEQCOMDupireHestonGlobal',tvar,x, eqHeston.maxIter, options,'unc',eqHeston,optParams);
                    
                    if ret == -1
                        tvar(1) = eqHeston.modelParams('kappa');
                        tvar(2) = eqHeston.modelParams('theta');
                        tvar(3) = eqHeston.modelParams('rho');
                        tvar(4) = eqHeston.modelParams('sigma');
                        tvar(5) = eqHeston.modelParams('v0');
                        x=  zeros(optParams.numOfEquation,1);
                        
                        [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, 10, options,'bc',lb,ub,eqHeston,optParams);
                    
                    elseif ~BoundaryConditionCheck(eqHeston,popt,lb,ub)
                        tvar(1) = eqHeston.modelParams('kappa');
                        tvar(2) = eqHeston.modelParams('theta');
                        tvar(3) = eqHeston.modelParams('rho');
                        tvar(4) = eqHeston.modelParams('sigma');
                        tvar(5) = eqHeston.modelParams('v0');
                        x=  zeros(optParams.numOfEquation,1);
                        
                        [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, 10, options,'bc',lb,ub,eqHeston,optParams);
                    
                            
                    end
%                     [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, eqHeston.maxIter, options,'bc',lb,ub,eqHeston,optParams);
                    
                    toc
                    
                    eqHeston.kappa = popt(1);
                    eqHeston.theta = popt(2);
                    eqHeston.rho   = popt(3);
                    eqHeston.sigma = popt(4);
                    eqHeston.v0    = popt(5);
                    
                    out.kappa = popt(1);
                    out.theta = popt(2);
                    out.rho = popt(3);
                    out.sigma = popt(4);
                    out.v0 = popt(5);
                    
                    out.paramsOut = zeros(5,1);
                    out.paramsOut(1) = out.kappa;
                    out.paramsOut(2) = out.theta;
                    out.paramsOut(3) = out.rho;
                    out.paramsOut(4) = out.sigma;
                    out.paramsOut(5) = out.v0;
                    
                    if  strcmp(params.calibrationErrorType,'impVolError')
                        for i=1:params.expirySize
%                            fwd = eqHeston.Fwd(spot,expiry(i));
                           fwd = 1.0;
                           
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPriceFwdMon(1.0,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice -1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    
                    elseif strcmp(params.calibrationErrorType,'priceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice- market_otmPrice;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                        
                    elseif strcmp(params.calibrationErrorType,'relativePriceErrorSS')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = (model_otmPrice/market_otmPrice - 1.0)*sqrt(expiry(i)/365.0);
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                            
                    elseif strcmp(params.calibrationErrorType,'relativePriceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice - 1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    else
                        disp('unImplemented')
                    end
                case 'globalGA'
                    
                    optParams.params = params;
                    optParams.modelParamsSize = 5;  % kappa, theta, rho, sigma, v0,
                    optParams.numOfEquation = params.expirySize*params.strikeSize + ...  % target opm options
                                              0;   % constraint
                    
                    tvar = zeros(optParams.modelParamsSize,1);
                    
                    tvar(1) = eqHeston.kappa;
                    tvar(2) = eqHeston.theta;
                    tvar(3) = eqHeston.rho;
                    tvar(4) = eqHeston.sigma;
                    tvar(5) = eqHeston.v0;
                    
                    % initial parameters costval
                   
                    
                    x=  zeros(optParams.numOfEquation,1);
                    lb = [0.0001,0.0001,-0.9999,0.0001,0.0001];
                    ub = [100.0,100.0,0.9999,100.0,100.0];
                    
                    optionsLevmar=[1E-03, 1E-25, 1E-25, 1E-25, 1E-25];
                    
%                     [ret, poptLevmar, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, eqHeston.maxIter, optionsLevmar,'unc',eqHeston,optParams);
                    
                    targetfun = @(x) TargetFunctionHestonGlobalGA(eqHeston,x,optParams);
                    
                    tic
%                     options = optimset('fmincon');
%                     options = optimset(options,'algorithm','interior-point');
%                     [parameters, fval] = fmincon(targetfun,tvar,[],[],[],[],lb,ub,[],options);


                    optionsGa = gaoptimset(@ga);
%                     optionsGa = gaoptimset(optionsGa,'InitialPopulation',[tvar';parameters']);
%                     optionsGa = gaoptimset(optionsGa,'InitialPopulation',[tvar';poptLevmar']);
                    
                    optionsGa = gaoptimset(optionsGa,'MutationFcn',@mutationadaptfeasible);
%                     [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, eqHeston.maxIter, options,'unc',eqHeston,optParams);
                    [popt,fval,exitflag,outut]=ga(targetfun,length(tvar),[],[],[],[],lb,ub,[],optionsGa);
%                     [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, eqHeston.maxIter, options,'bc',lb,ub,eqHeston,optParams);
                    
                    toc
                    
                    eqHeston.kappa = popt(1);
                    eqHeston.theta = popt(2);
                    eqHeston.rho   = popt(3);
                    eqHeston.sigma = popt(4);
                    eqHeston.v0    = popt(5);
                    
                    out.kappa = popt(1);
                    out.theta = popt(2);
                    out.rho = popt(3);
                    out.sigma = popt(4);
                    out.v0 = popt(5);
                    
                    out.paramsOut = zeros(5,1);
                    out.paramsOut(1) = out.kappa;
                    out.paramsOut(2) = out.theta;
                    out.paramsOut(3) = out.rho;
                    out.paramsOut(4) = out.sigma;
                    out.paramsOut(5) = out.v0;
                    
                    if  strcmp(params.calibrationErrorType,'impVolError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice -1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    
                    elseif strcmp(params.calibrationErrorType,'priceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice- market_otmPrice;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                        
                    elseif strcmp(params.calibrationErrorType,'relativePriceErrorSS')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = (model_otmPrice/market_otmPrice - 1.0)*sqrt(expiry(i)/365.0);
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                            
                    elseif strcmp(params.calibrationErrorType,'relativePriceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice - 1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    else
                        disp('unImplemented')
                    end
                case 'globalKappaFixed'
                    
                    optParams.params = params;
                    optParams.modelParamsSize = 4;  % kappa is fixed so  theta, rho, sigma, v0,
                    optParams.numOfEquation = params.expirySize*params.strikeSize + ...  % target opm options
                                              0;   % constraint
                    
                    tvar = zeros(optParams.modelParamsSize,1);
                    
%                     tvar(1) = eqHeston.kappa;
                    tvar(1) = eqHeston.theta;
                    tvar(2) = eqHeston.rho;
                    tvar(3) = eqHeston.sigma;
                    tvar(4) = eqHeston.v0;
                    
                    % initial parameters costval
%                     options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
%                     x=  zeros(optParams.numOfEquation,1);
%                     lb = [0.0001,0.0001,-0.9999,0.0001,0.0001];
%                     ub = [100.0,100.0,0.9999,100.0,100.0];
                     
                    options=[1E-03,1E-17, 1E-17, 1E-17, 1E-11];
                    
                    x=  zeros(optParams.numOfEquation,1);
                    % one constraint for theta added
%                     x=  zeros(optParams.numOfEquation + 1,1);
                    
                    lb = [0.0001,-0.9999,0.0001,0.0001];
                    ub = [100.0,0.9999,100.0,100.0];
                    
                    tic
                    [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobalKappaFixed',tvar,x, eqHeston.maxIter, options,'unc',eqHeston,optParams);
                    
                    if ret == -1
                        tvar(1) = eqHeston.theta;
                        tvar(2) = eqHeston.rho;
                        tvar(3) = eqHeston.sigma;
                        tvar(4) = eqHeston.v0;
                        x=  zeros(optParams.numOfEquation,1);
                        [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobalKappaFixed',tvar,x, 10, options,'bc',lb,ub,eqHeston,optParams);
                     elseif ~BoundaryConditionCheck(eqHeston,popt,lb,ub)
                        tvar(1) = eqHeston.modelParams('theta');
                        tvar(2) = eqHeston.modelParams('rho');
                        tvar(3) = eqHeston.modelParams('sigma');
                        tvar(4) = eqHeston.modelParams('v0');
                        x=  zeros(optParams.numOfEquation,1);
                        [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobalKappaFixed',tvar,x, 10, options,'bc',lb,ub,eqHeston,optParams);
                     
                    end
%                     [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, eqHeston.maxIter, options,'bc',lb,ub,eqHeston,optParams);
                    
                    toc
                    
%                     eqHeston.kappa = popt(1);
                    eqHeston.theta = popt(2-1);
                    eqHeston.rho   = popt(3-1);
                    eqHeston.sigma = popt(4-1);
                    eqHeston.v0    = popt(5-1);
                    
                    out.kappa = eqHeston.kappa;
                    
                    out.theta = popt(2-1);
                    out.rho = popt(3-1);
                    out.sigma = popt(4-1);
                    out.v0 = popt(5-1);
                    
                    out.paramsOut = zeros(5,1);
                    out.paramsOut(1) = out.kappa;
                    out.paramsOut(2) = out.theta;
                    out.paramsOut(3) = out.rho;
                    out.paramsOut(4) = out.sigma;
                    out.paramsOut(5) = out.v0;
                    
                    if  strcmp(params.calibrationErrorType,'impVolError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice -1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    
                    elseif strcmp(params.calibrationErrorType,'priceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice- market_otmPrice;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                        
                    elseif strcmp(params.calibrationErrorType,'relativePriceErrorSS')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = (model_otmPrice/market_otmPrice - 1.0)*sqrt(expiry(i)/365.0);
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                            
                    elseif strcmp(params.calibrationErrorType,'relativePriceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice - 1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    else
                        disp('unImplemented')
                    end
                case 'globalKappaConstrained'
                    
                    optParams.params = params;
                    optParams.modelParamsSize = 5;  % kappa , rho, sigma, v0,
                    optParams.numOfEquation = params.expirySize*params.strikeSize + ...  % target opm options
                                              1;   % constraint
                    
                    tvar = zeros(optParams.modelParamsSize,1);
                    
                    tvar(1) = eqHeston.kappa;
                    tvar(2) = eqHeston.theta;
                    tvar(3) = eqHeston.rho;
                    tvar(4) = eqHeston.sigma;
                    tvar(5) = eqHeston.v0;
                    
                    % initial parameters costval
%                     options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
%                     x=  zeros(optParams.numOfEquation,1);
%                     lb = [0.0001,0.0001,-0.9999,0.0001,0.0001];
%                     ub = [100.0,100.0,0.9999,100.0,100.0];
                     
                    options=[1E-03,1E-17, 1E-17, 1E-17, 1E-11];
                    x=  zeros(optParams.numOfEquation,1);
                    lb = [0.0001,0.0001,-0.9999,0.0001,0.0001];
                    ub = [100.0,100.0,0.9999,100.0,100.0];
                    
                    tic
                    [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobalKappaConstrained',tvar,x, eqHeston.maxIter, options,'unc',eqHeston,optParams);

%                     [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobalKappaFixed',tvar,x, eqHeston.maxIter, options,'unc',eqHeston,optParams);
%                     [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, eqHeston.maxIter, options,'bc',lb,ub,eqHeston,optParams);
                    
                    toc
                    
                    eqHeston.kappa = popt(1);
                    eqHeston.theta = popt(2);
                    eqHeston.rho   = popt(3);
                    eqHeston.sigma = popt(4);
                    eqHeston.v0    = popt(5);
                    
                    out.kappa = popt(1);
                    out.theta = popt(2);
                    out.rho = popt(3);
                    out.sigma = popt(4);
                    out.v0 = popt(5);
                    
                    out.paramsOut = zeros(5,1);
                    out.paramsOut(1) = out.kappa;
                    out.paramsOut(2) = out.theta;
                    out.paramsOut(3) = out.rho;
                    out.paramsOut(4) = out.sigma;
                    out.paramsOut(5) = out.v0;
                    
                    if  strcmp(params.calibrationErrorType,'impVolError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice -1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    
                    elseif strcmp(params.calibrationErrorType,'priceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice- market_otmPrice;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                        
                    elseif strcmp(params.calibrationErrorType,'relativePriceErrorSS')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = (model_otmPrice/market_otmPrice - 1.0)*sqrt(expiry(i)/365.0);
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                            
                    elseif strcmp(params.calibrationErrorType,'relativePriceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice - 1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    else
                        disp('unImplemented')
                    end
                    
                case 'JustCalculateError'
                    
%                     optParams.params = params;
%                     optParams.modelParamsSize = 5;  % kappa, theta, rho, sigma, v0,
%                     optParams.numOfEquation = params.expirySize*params.strikeSize + ...  % target opm options
%                                               0;   % constraint
%                     
%                     tvar = zeros(optParams.modelParamsSize,1);
%                     
%                     tvar(1) = eqHeston.kappa;
%                     tvar(2) = eqHeston.theta;
%                     tvar(3) = eqHeston.rho;
%                     tvar(4) = eqHeston.sigma;
%                     tvar(5) = eqHeston.v0;
                    
%                     % initial parameters costval
% %                     options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-11];
%                     options=[1E-03, 1E-25, 1E-25, 1E-25, 1E-25];
%                     x=  zeros(optParams.numOfEquation,1);
%                     lb = [0.0001,0.0001,-0.9999,0.0001,0.0001];
%                     ub = [100.0,100.0,0.9999,100.0,100.0];
%                     tic
%                     [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, eqHeston.maxIter, options,'unc',eqHeston,optParams);
% %                     [ret, popt, info, covar]=levmar('TargetFunctionHestonGlobal',tvar,x, eqHeston.maxIter, options,'bc',lb,ub,eqHeston,optParams);
%                     
%                     toc
%                     
%                     eqHeston.kappa = popt(1);
%                     eqHeston.theta = popt(2);
%                     eqHeston.rho   = popt(3);
%                     eqHeston.sigma = popt(4);
%                     eqHeston.v0    = popt(5);
                    
                    out.kappa = eqHeston.kappa;
                    out.theta = eqHeston.theta;
                    out.rho = eqHeston.rho;
                    out.sigma = eqHeston.sigma;
                    out.v0 = eqHeston.v0;
                    
                    out.paramsOut = zeros(5,1);
                    out.paramsOut(1) = out.kappa;
                    out.paramsOut(2) = out.theta;
                    out.paramsOut(3) = out.rho;
                    out.paramsOut(4) = out.sigma;
                    out.paramsOut(5) = out.v0;
                    
                    if  strcmp(params.calibrationErrorType,'impVolError')
                        for i=1:params.expirySize
%                            fwd = eqHeston.Fwd(spot,expiry(i));
                            fwd = 1.0;
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPriceFwdMon(1.0,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice -1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    
                    elseif strcmp(params.calibrationErrorType,'priceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice- market_otmPrice;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                        
                    elseif strcmp(params.calibrationErrorType,'relativePriceErrorSS')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = (model_otmPrice/market_otmPrice - 1.0)*sqrt(expiry(i)/365.0);
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                            
                    elseif strcmp(params.calibrationErrorType,'relativePriceError')
                        for i=1:params.expirySize
                           fwd = eqHeston.Fwd(spot,expiry(i));
                            for j=1:params.strikeSize
                                market_vol = params.blackVol(i,j);
                                market_otmPrice = params.blackOTMPrice(i,j);
                                marketStrike = params.marketStrikes(i,j);
                                model_otmPrice = eqHeston.modelOTMPrice(spot,marketStrike,expiry(i));
                                model_vol = eqHeston.ImpliedBlackVol(model_otmPrice,fwd,marketStrike,expiry(i)/365.0);
                                out.re(i,j) = model_otmPrice/market_otmPrice - 1.0;
                                out.hestonBlackVol(i,j) = model_vol;
                                out.voldiff(i,j) = model_vol - market_vol;
                                out.hestonOTMPrice(i,j) = model_otmPrice;
                            end
                        end

                        N=0;
                        for j=1:expirySize
                            for k=1:strikeSize
                                if params.calibrationYN(j,k) == 1
                                    out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                                    out.volmseTotal = out.volmseTotal + out.voldiff(j,k)*out.voldiff(j,k);
                                    N=N+1;
                                end
                            end
                        end

                        out.rmseTotal = sqrt(out.rmseTotal/N);
                        out.volmseTotal = sqrt(out.volmseTotal/N);
                    else
                        disp('unImplemented')
                    end
                    
                otherwise
                    disp('unImplemented')
            end
        end 
             
    end
    
end



In [ ]:
classdef EQCOMDupire < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        % vol functor
        impliedVolSurface
        localVolSurface
        volProxy
    end
    
    methods
        function eqDupire = EQCOMDupire(EQModel)
            if nargin > 0
                eqDupire.zeroCurve = EQModel.zeroCurve;
                eqDupire.dividendCurve = EQModel.dividendCurve;
                eqDupire.repoRateCurve = EQModel.repoRateCurve;
                eqDupire.forwardCurve = EQModel.forwardCurve;
                eqDupire.spot = EQModel.spot;
                eqDupire.mktData =  EQModel.mktData;
                eqDupire.modelParams = EQModel.modelParams;
                eqDupire.impliedVolSurface = eqDupire.mktData('impliedVolSurface');
                eqDupire.localVolSurface = EQModel.modelParams('localVolSurface');
                
            end
        end
        
        function out = TDMASolve(eqDupire,tdma,vector)
            size = tdma.size;
            out = vector;
            
            for i=2:size
                out(i) = out(i) - tdma.ll(i)*out(i-1);
            end
            
            out(size) = out(size)/tdma.dd(size);
            
            for i=size-1:-1:1
                out(i) = (out(i) - out(i+1)*tdma.uu(i))/tdma.dd(i);
            end
            
        end
        
        function out = LUDecompose(eqDupire,tdma)
            out = tdma;
            if out.bupdated == 1
                for i=1:out.size
                    out.uu(i) = out.c(i);
                end
                
                out.dd(1) = out.b(1);
                for i=2:out.size
                    out.ll(i) = out.a(i)/out.dd(i-1);
                    out.dd(i) = out.b(i) - out.c(i-1)*out.ll(i);
                end
                
                out.bupdated = 0;
            end
        
        end
        
        function [newC newP] = Solve1DPDE(eqDupire,tvar,dT,dK,lastC,lastP,optParams)
            
            %filling proxy grid vol
            proxy = zeros(length(lastC),1);
            
            for i=1: length(tvar)
%                 Extrapolation at the left and right
                if i == 1
                    for j=1:optParams.ipos(i)-1
                        proxy(j) = tvar(i);
                    end
                elseif i == length(tvar)
                    for j=optParams.ipos(i-1):optParams.ipos(i)-1
                        proxy(j) = (optParams.Ks(j)-optParams.Ks(optParams.ipos(i-1)))*(tvar(i)-tvar(i-1))/(optParams.Ks(optParams.ipos(i))-optParams.Ks(optParams.ipos(i-1))) + tvar(i-1);
                    end
                    for j=optParams.ipos(i):length(lastC)
                        proxy(j) = tvar(i);
                    end
%                  linear interpolation in the log grid in-between    
                else
                    for j=optParams.ipos(i-1):optParams.ipos(i)-1
                        proxy(j) = (optParams.Ks(j)-optParams.Ks(optParams.ipos(i-1)))*(tvar(i)-tvar(i-1))/(optParams.Ks(optParams.ipos(i))-optParams.Ks(optParams.ipos(i-1))) + tvar(i-1);
                    end
                end
            end
           
            proxy(length(lastC)) = tvar(length(tvar));
            
            %filling end
            
            meshC = lastC;
            meshP = lastP;
            
            tdma.size = length(meshC);
            tdma.bupdated = 0;
            tdma.a = zeros(tdma.size,1);
            tdma.b = zeros(tdma.size,1);
            tdma.c = zeros(tdma.size,1);
            tdma.uu = zeros(tdma.size,1);
            tdma.ll = zeros(tdma.size,1);
            tdma.dd = zeros(tdma.size,1);
            
            for i=2:tdma.size-1
                temp = 0.5*dT*proxy(i)*proxy(i)/dK;
                tdma.a(i) = -temp*(1/dK + 0.5);
                tdma.b(i) = 1 + 2.0/dK*temp;
                tdma.c(i) = -temp*(1/dK - 0.5);
            end
            
            tdma.a(1) = 0;
            tdma.a(tdma.size) = 0;
            tdma.c(1) = 0;
            tdma.c(tdma.size) = 0;
            tdma.b(1) = 1;
            tdma.b(tdma.size) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqDupire.LUDecompose(tdma);
            pmeshC = eqDupire.TDMASolve(tdmaLU,meshC);
            newC = pmeshC;
            
            pmeshP = eqDupire.TDMASolve(tdmaLU,meshP);
            newP = pmeshP;
        end
        
        function out = InterpolateTargetStrikeVol(eqDupire,idxNow,meshC,meshP,params)
            % Calculate Object Function
            % settings for bisection
            a = 0.001;
            b = 10;
            Tol = 1e-10;
            MaxIter = 1000;

            out.strikes = params.targetStrikes;
            strikeSize = length(params.targetStrikes);
            out.vols    = zeros(strikeSize,1);
            out.interpOTMPrices = zeros(strikeSize,1);
            lnK = 0.0;
            for i=1:strikeSize
                K = out.strikes(i);
                lnK = log(K);
                %linear interpolated option values
                NGP = round((lnK-params.Ks(1))/params.dK);
                % corrected distance index
                NGP = NGP +1;
                if NGP < 1
                    NGP = 1;
                elseif NGP >= params.Ns
                    NGP = params.Ns-1;
                end

                alpha = (lnK-params.Ks(NGP))/params.dK;
                cValue = (1-alpha)*meshC(NGP) + alpha*meshC(NGP+1);
                pValue = (1-alpha)*meshP(NGP) + alpha*meshP(NGP+1);
                if K <= 1.0
                     out.vols(i) = BisecBlackFwdIV('P',1.0,K, ...
                                          0.0,params.expiry(idxNow)/365.0,a,b,pValue,Tol,MaxIter);
                     out.interpOTMPrices(i) = pValue;
                else
                    out.vols(i) = BisecBlackFwdIV('C',1.0,K, ...
                                          0.0,params.expiry(idxNow)/365.0,a,b,cValue,Tol,MaxIter);
                    out.interpOTMPrices(i) = cValue;
                end
            end
            
            
        end
        
        function out = CalculateTarget(eqDupire,idxNow,meshC,meshP,optParams)
            % Calculate Object Function
            
            out.dupireOTMPrice = zeros(optParams.strikeSize,1);
            out.re = zeros(optParams.strikeSize,1);
            
            for i=1:optParams.strikeSize
                K = optParams.marketStrikes(i);
                %linear interpolated option values
                NGP = round((K-optParams.Ks(1))/optParams.dK);
                % corrected distance index
                NGP = NGP +1;
                if NGP < 1
                    NGP = 1;
                elseif NGP >= optParams.meshSize
                    NGP = optParams.meshSize-1;
                end

                alpha = (K-optParams.Ks(NGP))/optParams.dK;
                cValue = (1-alpha)*meshC(NGP) + alpha*meshC(NGP+1);
                pValue = (1-alpha)*meshP(NGP) + alpha*meshP(NGP+1);
                if K <= 0
                    out.re(i) = pValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                    out.dupireOTMPrice(i) = pValue;
                else
                    out.re(i) = cValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                    out.dupireOTMPrice(i) = cValue;
                end
            end
            
            
        end
        
        function  out  = TargetFunctionVolProxyLevMar(tvar,eqDupire,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            %filling vol proxy grid with the tvar
          %% Solve  Forward PDE One time
            [newC newP] = eqDupire.Solve1DPDE(tvar,mkt_dT,optParams.dK,optParams.lastC,optParams.lastP,optParams);
            optParams.meshC = newC;
            optParams.meshP = newP;
           %% PDE Solve End
            target = CalculateTarget(eqDupire,idxNow,newC,newP,optParams);
            out = target.re;
        end
        
        function  out  = TargetFunctionVolProxy(eqDupire,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            %filling vol proxy grid with the tvar
          %% Solve  Forward PDE One time
            [newC newP] = eqDupire.Solve1DPDE(tvar,mkt_dT,optParams.dK,optParams.lastC,optParams.lastP,optParams);
            optParams.meshC = newC;
            optParams.meshP = newP;
           %% PDE Solve End
            target = CalculateTarget(eqDupire,idxNow,newC,newP,optParams);
            out = 0.0;
            for i=1:length(target.re)
                out = out + target.re(i)*target.re(i);
            end
        end
        
        function  out  = TargetFunctionVolProxyOld(eqDupire,tvar,optParams)
            idxNow = optParams.idxNow;
            if  idxNow ~= 1 mkt_dT = optParams.params.expiry(idxNow) - optParams.params.expiry(idxNow-1);else mkt_dT =  optParams.params.expiry(1);end;
            mkt_dT=mkt_dT/365.0;
            %filling vol proxy grid with the tvar
            proxy = zeros(optParams.meshSize,1);
            
            for i=1: optParams.strikeSize
                if i == 1
                    for j=1:optParams.ipos(i)-1
                        proxy(j) = tvar(i);
                    end
                elseif i == optParams.strikeSize
                    for j=optParams.ipos(i-1):optParams.ipos(i)-1
                        proxy(j) = tvar(i);
                    end 
                else
                    for j=optParams.ipos(i-1):optParams.ipos(i)-1
                        proxy(j) = tvar(i);
                    end
                end
            end
           
            proxy(optParams.meshSize) = tvar(optParams.strikeSize);
            
            % Solve  Forward PDE One time
            optParams.meshC = optParams.lastCurveC;
            optParams.meshP = optParams.lastCurveP;
            
            tdma.size = optParams.meshSize;
            tdma.bupdated = 0;
            tdma.a = zeros(optParams.meshSize,1);
            tdma.b = zeros(optParams.meshSize,1);
            tdma.c = zeros(optParams.meshSize,1);
            tdma.uu = zeros(optParams.meshSize,1);
            tdma.ll = zeros(optParams.meshSize,1);
            tdma.dd = zeros(optParams.meshSize,1);
            
            for i=2:optParams.meshSize-1
                temp = 0.5*mkt_dT*proxy(i)*proxy(i)/optParams.dK;
                tdma.a(i) = -temp*(1/optParams.dK + 0.5);
                tdma.b(i) = 1 + 2.0/optParams.dK*temp;
                tdma.c(i) = -temp*(1/optParams.dK - 0.5);
            end
            
            tdma.a(1) = 0;
            tdma.a(optParams.meshSize) = 0;
            tdma.c(1) = 0;
            tdma.c(optParams.meshSize) = 0;
            tdma.b(1) = 1;
            tdma.b(optParams.meshSize) = 1;
            tdma.bupdated = 1;
            
            tdmaLU =  eqDupire.LUDecompose(tdma);
            pmeshC = eqDupire.TDMASolve(tdmaLU,optParams.meshC);
            optParams.meshC = pmeshC;
            
            pmeshP = eqDupire.TDMASolve(tdmaLU,optParams.meshP);
            optParams.meshP = pmeshP;
            % PDE Solve End
         
            % Calculate Object Function
            target = zeros(optParams.strikeSize,1);
         
            for i=1:optParams.strikeSize
                K = optParams.marketStrikes(i);
                %linear interpolated option values
                NGP = round((K-optParams.Ks(1))/optParams.dK);
                % corrected distance index
                NGP = NGP +1;
                if NGP < 1
                    NGP = 1;
                elseif NGP >= optParams.meshSize
                    NGP = optParams.meshSize-1;
                end

                alpha = (K-optParams.Ks(NGP))/optParams.dK;
                cValue = (1-alpha)*optParams.meshC(NGP) + alpha*optParams.meshC(NGP+1);
                pValue = (1-alpha)*optParams.meshP(NGP) + alpha*optParams.meshP(NGP+1);
                optParams.callCurve(i) = cValue;
                optParams.putCurve(i) = pValue;
                if K <= 0
                    target(i) = pValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                else
                    target(i) = cValue/optParams.blackOTMPrice(idxNow,i) - 1.0;
                end
            end
            
            out = 0;
            for i=1:optParams.strikeSize
                out = out + target(i)*target(i)*10000;
            end
        end
        
        function bootStrapOut = FindVolProxy(eqDupire,idxNow,dT,lastC,lastP,params)
            %initialize calibration parameters
            
            for i=1:params.strikeSize
%                 tvar(i) = params.volSurface.vol(params.expiry(idxNow),params.strike(i));
                tvar(i) = params.volSurface.volSurfaceR(idxNow,i);
                
                lb(i) = 0.01;
                ub(i) = 1.0;
            end
            
            optParams.idxNow = idxNow;
            optParams.dT = dT;
            optParams.params = params;
            optParams.ipos = zeros(params.strikeSize,1);
            optParams.Ks = zeros(params.Ns,1);
            optParams.Ks = params.Ks;
            optParams.strikeSize = params.strikeSize;
            optParams.meshSize = params.Ns;
            optParams.meshC = zeros(params.Ns,1);
            optParams.meshP = zeros(params.Ns,1);
            optParams.proxy = zeros(params.Ns,1);
            optParams.dK = params.Ks(2) - params.Ks(1);
            optParams.marketStrikes = zeros(params.strikeSize,1);
            optParams.blackOTMPrice = params.blackOTMPrice;
            optParams.callCurve = zeros(params.strikeSize,1);
            optParams.putCurve = zeros(params.strikeSize,1);
            
            for i=1:params.strikeSize
                optParams.marketStrikes(i) = log(params.fwdMoneyness(idxNow,i));
            end
            
%             if strcmp(params.volSurface.params('moneyNessType'),'spotMoneyNess')
%                 % market strike points in fwd PDE grid
%                 fwdFactor = eqDupire.FwdFactor(params.expiry(idxNow));
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = log(params.strike(i)/fwdFactor);
%                 end
%             else
%                 for i=1:params.strikeSize
%                     optParams.marketStrikes(i) = log(params.strike(i));
%                 end
%             end
            
            % positions to separate vol proxy regimes
            for i=1:params.strikeSize
                optParams.ipos(i) = round( (optParams.marketStrikes(i) - optParams.Ks(1))/optParams.dK);
            end
%             optParams.ipos(params.strikeSize) = optParams.meshSize;
            
            optParams.lastC = lastC;
            optParams.lastP = lastP;
            
            targetfun = @(tvar) TargetFunctionVolProxy(eqDupire,tvar,optParams);
%             options=optimset('Algorithm','trust-region-reflective');
%             [x, fval] = fmincon(targetfun,tvar,[],[],[],[],lb,ub,[]);
%             [x, fval] = fminsearch(targetfun,tvar);
            
%             [x, fval] = fmincon(targetfun,tvar,[],[],[],[],lb,ub,[],options);
%             [x,fval,exitflag,output1,lambda,grad,hessian] = fmincon(targetfun,tvar,[],[],[],[],lb,ub,[],options);

            options=[1E-03, 1E-25, 1E-25, 1E-25, 1E-25];
            x=  zeros(params.strikeSize,1);
            [ret, popt, info, covar]=levmar('TargetFunctionVolProxyLevMar1',tvar,x, 200, options,'unc',eqDupire,optParams);
            %Levenberg Marquardt Algorithm
            
%             targetfun = @(tvar) TargetFunctionVolProxyLevMar(eqDupire,tvar,optParams);
%             options=optimset('Algorithm','levenberg-marquardt');
%             [x, fval] = lsqnonlin(targetfun,tvar,lb,ub,options);
%             
%             targetfun = @(t) eqDupire.TargetFunctionVolProxyLevMar(t,optParams);
%             t0 = tvar;
%             options=optimset('Algorithm','levenberg-marquardt');
%             [x, fval] = lsqnonlin(targetfun,tvar,lb,ub,options);
%             x = zeros(1,params.strikeSize);
%             options=[1E-03, 1E-15, 1E-15, 1E-20, 1E-06];
% %             [ret, x, info]=levmar('targetfun', t0, x, 200, options, optParams);
%             [ret, popt, info]=levmar('targetfun', t0, x, 200, options);
            
            
            % min vol 0.0001
            minVol = 0.0001;
            for i=1:params.strikeSize
                bootStrapOut.volProxy(i) = max(popt(i),minVol);
%                 bootStrapOut.volProxy(i) = popt(i);
                bootStrapOut.ipos(i) = optParams.ipos(i);
            end
            
            [newC newP] = eqDupire.Solve1DPDE(bootStrapOut.volProxy,dT,optParams.dK,lastC,lastP,optParams);
            target = eqDupire.CalculateTarget(idxNow,newC,newP,optParams);
            
            bootStrapOut.lastC = newC;
            bootStrapOut.lastP = newP;
            
            bootStrapOut.re = target.re;
            bootStrapOut.dupireOTMPrice = target.dupireOTMPrice;
            
        end
        
        function out = CalibrateToVolSurface(eqDupire,black,calibrationFlag)
            
          % Calculate Black OTM Prices as calibration target
            volSurface = black.volSurface;
            
            expiry = volSurface.maturities;
            strike  = volSurface.strikes;
            spot =  black.spot.params('rawData');
            expirySize = length(expiry);
            strikeSize = length(strike);
            
            blackOTMPrice = zeros(expirySize,strikeSize);
            for k=1:expirySize
                for j=1:strikeSize
                    blackVol(k,j) = volSurface.volSurfaceR(k,j);
                    if strike(j) <= 0
                        dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                        fwdMoneyness(k,j) = exp(norminv(-1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
%                         blackOTMPrice(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                    else
                        dummyStd = blackVol(k,j)*sqrt(expiry(k)/365.0);
                        fwdMoneyness(k,j) = exp(-1.0*norminv(1.0*strike(j),0,1)*dummyStd+0.5*dummyStd*dummyStd);
%                         blackOTMPrice(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');

                    end
                    
                    if fwdMoneyness(k,j) <= 1.0
                        blackOTMPrice(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'P');
                    else
                        blackOTMPrice(k,j) = black.BlackVanillaFwd(expiry(k),1.0,fwdMoneyness(k,j),blackVol(k,j),'C');
                    end
                end
            end
%             if strcmp(volSurface.params('moneyNessType'),'spotMoneyNess')
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     fwdFactor = black.FwdFactor(expiry(k));
%                     for j=1:strikeSize
%                         fwdStrike = strike(j)/fwdFactor;
%                         if fwdStrike <= 1
%                             blackOTMPrice(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                         else
%                             blackOTMPrice(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,spot*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                         end
%                     end
%                 end
%             else
%                 for k=1:expirySize
%                     fwd = black.Fwd(spot,expiry(k));
%                     df = black.zeroCurve.DF(expiry(k)/365.0);
%                     for j=1:strikeSize
%                         if strike(j) <= 1
%                             blackOTMPrice(k,j) = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'P')/fwd/df;
%                         else
%                             blackOTMPrice(k,j)  = black.BlackVanilla(expiry(k),expiry(k),spot,fwd*strike(j),volSurface.vol(expiry(k),strike(j)),'C')/fwd/df;
%                         end
%                     end
%                 end
%             end
            
            
            params.volSurface = volSurface;
            params.expiry = expiry;
            params.strike = strike;
            params.fwdMoneyness = fwdMoneyness;
            
            
            params.blackOTMPrice = blackOTMPrice;
            
            params.expirySize = expirySize;
            params.strikeSize =  strikeSize;
            
            % vol proxy calibration grid setting
            params.Kmin = 0.1;
            params.Kmax = 2.5;
            params.Ns = 1001;
            params.Nt = 1;
            params.dK = (log(params.Kmax) - log(params.Kmin))/(params.Ns-1);
            for i=1:params.Ns
                params.Ks(i) = log(params.Kmin) + params.dK*(i-1);
            end
            
            %output vol proxy
            
            out.volProxy = zeros(params.expirySize,params.strikeSize);
            out.ipos = zeros(params.expirySize,params.strikeSize);
            out.callMesh = zeros(params.expirySize,params.Ns);
            out.putMesh = zeros(params.expirySize,params.Ns);
            % output localvol setting
            out.dK = params.dK;
            out.localVolSurface.strikeSize = params.Ns;
            out.Ks = zeros(params.Ns,1);
            for i=1:params.Ns
                out.Ks(i) = log(params.Kmin) + out.dK*(i-1);
            end
            
            out.dt = params.Nt/365.0;
            out.localVolSurface.expirySize = round(params.expiry(expirySize)/365.0/out.dt + 0.5) +1;
            out.localVolSurface.expiry = zeros(out.localVolSurface.expirySize,1);
            for i=1:out.localVolSurface.expirySize
                out.localVolSurface.expiry(i) = i*out.dt;
            end
            
            for i=1:out.localVolSurface.strikeSize
                for j=1:out.localVolSurface.expirySize
                    out.localVolSurface.vol(i,j) = 0.0;
                end
            end
            
            
            %initialze the intial call & put payoff in fwd PDE grid
            initC = zeros(params.Ns,1);
            initP = zeros(params.Ns,1);
            for i=1:params.Ns
                initC(i) = max(1-exp(out.Ks(i)),0.0);
                initP(i) = max(exp(out.Ks(i))-1,0.0);
            end
            
            out.blackOTMPrice = blackOTMPrice;
            out.dupireOTMPrice = zeros(expirySize,strikeSize);
            out.re = zeros(expirySize,strikeSize);
            out.rmseTotal=0.0;
            
            
            calibrationType = 'bootstrap';
            if nargin < 3
                calibrationType = 'bootstrap'; 
            else
                calibrationType = calibrationFlag;
            end
            
            switch calibrationType
                case 'bootstrap'
                    %vol proxy calibration
                    lastC = initC;
                    lastP = initP;
                    
                    for i=1:expirySize
                        if  i ~= 1 dT = params.expiry(i) - params.expiry(i-1);else dT =  params.expiry(i);end;
                        dT = dT/365.0;
                        bootStrapOut = eqDupire.FindVolProxy(i,dT,lastC,lastP,params);
                        for j=1:strikeSize
                            out.volProxy(i,j) = bootStrapOut.volProxy(j);
                            out.ipos(i,j)     = bootStrapOut.ipos(j);
                            out.re(i,j) = bootStrapOut.re(j);
                            out.dupireOTMPrice(i,j) = bootStrapOut.dupireOTMPrice(j);
                        end
                        
                        for j=1:params.Ns
                            out.callMesh(i,j) = bootStrapOut.lastC(j);
                            out.putMesh(i,j) = bootStrapOut.lastP(j);
                        end
                        % Initial Payoff for the next period
                        lastC = bootStrapOut.lastC;
                        lastP = bootStrapOut.lastP;
                        
                    end
                    
                    N=0;
                    for j=1:expirySize
                        for k=1:strikeSize
                            out.rmseTotal = out.rmseTotal + out.re(j,k)*out.re(j,k);
                            N=N+1;
                        end
                    end
                   
                    out.rmseTotal = sqrt(out.rmseTotal/N);
                    
                    
                    targetStrikes = 0.3:0.05:1.8;
                    params.targetStrikes = targetStrikes;
                    out.targetStrikes = zeros(expirySize,length(targetStrikes));
                    out.targetVols = zeros(expirySize,length(targetStrikes));
                    out.interpOTMPrices = zeros(expirySize,length(targetStrikes));
                    
                    for i=1:expirySize
                        target = eqDupire.InterpolateTargetStrikeVol(i,out.callMesh(i,:),out.putMesh(i,:),params);
                        for j=1:length(targetStrikes)
                            out.targetStrikes(i,j) = target.strikes(j);
                            out.targetVols(i,j) = target.vols(j);
                            out.interpOTMPrices(i,j) = target.interpOTMPrices(j);
                        end
                    end
                    
                otherwise
                    disp('unImplemented')
            end
        end 
             
    end
    
end



In [ ]:
classdef EQBS_CK1FSimple < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        % vol functor
        domestic_meanR_r;
        
        domestic_vol_r;
        
        %market input
        corr_de;
        
        %modelParams
        corr_dre;
        
        eqBlackVol;
        
        numOfFactors;
        modelType;
%         freq;
    end
    
    methods
        function eqDuire_ck1f = EQBS_CK1FSimple(params)
            if nargin > 0
                eqDuire_ck1f.zeroCurve = params.eqModel.zeroCurve;
%                 eqDuire_ck1f.freq = params.eqModel.freq;
                eqDuire_ck1f.zeroCurve = params.eqModel.zeroCurve;
                eqDuire_ck1f.dividendCurve = params.eqModel.dividendCurve;
                eqDuire_ck1f.repoRateCurve = params.eqModel.repoRateCurve;
                eqDuire_ck1f.forwardCurve = params.eqModel.forwardCurve;
                
                eqDuire_ck1f.spot = params.eqModel.spot;
                eqDuire_ck1f.mktData =  params.eqModel.mktData;
                eqDuire_ck1f.modelParams = params.eqModel.modelParams;
                
                
                eqDuire_ck1f.numOfFactors = 1;
                eqDuire_ck1f.modelType = 'eqDuire_ck1f';
                
                eqDuire_ck1f.domestic_meanR_r = params.domesticModel.meanR_r;
                
                if params.eqVolCalibrated == true
                    % we do not calibrate eqBlackVol
                    eqDuire_ck1f.corr_de = params.corr_de;
                    
                    out = eqDuire_ck1f.synchronizeModelParams(params);
                                        
                    eqDuire_ck1f.corr_dre.tenor = out.sigmaTimes;
                    eqDuire_ck1f.corr_dre.quote = out.corr_dre_Values;
                    
                    eqDuire_ck1f.domestic_vol_r.tenor = out.sigmaTimes;
                    eqDuire_ck1f.domestic_vol_r.quote = out.domestic_vol_r_Values;
                                        
                    eqDuire_ck1f.eqBlackVol.tenor = out.sigmaTimes;
                    eqDuire_ck1f.eqBlackVol.quote = out.eqBlackVolValues;
                    
                else                    
                    % black vol calibration start
                    paramsIn.eqImpVol = params.eqBlackVol;
                    paramsIn.eqBlackVol = paramsIn.eqImpVol;
                    
                    paramsIn.domestic_meanR_r = params.domesticModel.meanR_r;
                    paramsIn.domestic_vol_r = params.domesticModel.vol_r;
                    
                    paramsIn.corr_de = params.corr_de;
                    
                    paramsIn.corr_dre = params.corr_dre;
                    
                     % BSCK1F Calibration Start
                    out = eqDuire_ck1f.CalibrateBSCK1FVol(paramsIn);
                    re =  out.re;
                    
                    marketVar = out.marketVar;
                    modelVar = out.modelVar;
                    rmseTotal = out.rmseTotal;
                    
                    % BSCK1F Calibration End
                    
                    params.eqBlackVol = out.eqBlackVol;
                    params.eqVolCalibrated =  true;
%                     eqDuire_ck1f = EQBS_CK1F(params);
                    eqDuire_ck1f = EQBS_CK1FSimple(params);
                    
                end
            end
        end
        
        function out =  synchronizeModelParams(eqDuire_ck1f, params)
            eqBlackVolTenor = params.eqBlackVol.tenor;
            eqBlackVolQuote = params.eqBlackVol.quote;

            % synchronize model parameters time-steps start
            corr_dre_Tenor = params.corr_dre.tenor;
            corr_dre_Quote = params.corr_dre.quote;
            
            domestic_vol_r_Tenor = params.domesticModel.vol_r.tenor;
            domestic_vol_r_Quote = params.domesticModel.vol_r.quote;

            sigmaTimes = unique(union([corr_dre_Tenor(:);...
                         domestic_vol_r_Tenor(:)], eqBlackVolTenor));

            sigmaTimes = sort(sigmaTimes,'ascend');
            
            corr_dre_Values = zeros(length(sigmaTimes),1);
            
            domestic_vol_r_Values = zeros(length(sigmaTimes), 1);
            
            eqBlackVolValues = zeros(length(sigmaTimes),1);
            
            for k=1:length(sigmaTimes)
                corr_dre_Values(k) = H_interpolation(corr_dre_Tenor, corr_dre_Quote,sigmaTimes(k), 0);
                
                domestic_vol_r_Values(k) = H_interpolation(domestic_vol_r_Tenor, domestic_vol_r_Quote, sigmaTimes(k), 0);
                eqBlackVolValues(k) = H_interpolation(eqBlackVolTenor, eqBlackVolQuote,sigmaTimes(k),0);
            
            end
            
            out.sigmaTimes = sigmaTimes;
            
            out.corr_dre_Values = corr_dre_Values;
            
            out.domestic_vol_r_Values = domestic_vol_r_Values;
            out.eqBlackVolValues = eqBlackVolValues;
            
        end
        
        function out =  Libor_SimpleDate(eqDuire_ck1f, valueDate, evalTime, fwdStartTime, numMatTime, tenor, modelStatesT)
           % foreign Libor in domestic Terminal measure
           fwdStartDate = valueDate.AddDate(fwdStartTime,'day');
           fwdEndDate = fwdStartDate.AddDate(tenor,'year');
           fwdEndTime = fwdEndDate.DateDiff(valueDate);
           
           deltaT = (fwdEndTime - fwdStartTime)/365.0;
           numMatDate = valueDate.AddDate(numMatTime,'day');
           
           stateSize = size(modelStatesT,2);
           df_Tn = zeros(1,stateSize);
           df_TN = zeros(1,stateSize);
           
           df_Tn = eqDuire_ck1f.discountFactor(evalTime, fwdStartTime, numMatTime, modelStatesT);
           df_TN = eqDuire_ck1f.discountFactor(evalTime, fwdEndTime, numMatTime, modelStatesT);
           
           liborOut = zeros(1, stateSize);
           
           for i = 1:stateSize
                liborOut(i) = (df_Tn(i) / df_TN(i) - 1.0) / deltaT;
           end
           
           out = liborOut;
            
        end
        
        function out = CMS_SimpleDate(eqDuire_ck1f, valueDate, observeTime, numMatTime, tenor, modelStatesT)
           % CMT
%            tau = 0.25;
           tau = 1.0 / (eqDuire_ck1f.freq);
           % if tenor is 0.25(3M) then use tenor(0.25) instead
           % model(zeroCurve)'s freq
           
           if abs(tenor - 0.25) < 1e-8
                tau = tenor;
           end
           
           to     = observeTime / 365.0;
           toDate = valueDate.AddDate(observeTime, 'day');
           tNDate = toDate.AddDate(tenor, 'year');
           tNTime = tNDate.DateDiff(valueDate);
           tN     =  tNTime / 365.0;
           
           numMatDate = valueDate.AddDate(numMatTime, 'day');
           
           addMonthUnit = round(12 * tau);
           cnt = round((tN - to) / tau);
           
           stateSize = size(modelStatesT, 2);
           
           annuity = zeros(1, stateSize);
           df_Tp = zeros(1, stateSize);           
           df_Tn = zeros(1, stateSize);
           df_TN = zeros(1, stateSize);
           
           for i = 1:cnt
               tpDate = toDate.AddDate(i * addMonthUnit,'month');
               tpTime = tpDate.DateDiff(valueDate);
               df_Tp = eqDuire_ck1f.discountFactor(observeTime, tpTime, numMatTime, modelStatesT);
               annuity = annuity + tau * df_Tp;
           end
           
           df_Tn = eqDuire_ck1f.discountFactor(observeTime, observeTime, numMatTime, modelStatesT);
           df_TN = eqDuire_ck1f.discountFactor(observeTime, tNTime, numMatTime, modelStatesT);
           
           cms_PCA_SimpleOut = zeros(1, stateSize);
           
           for i = 1:stateSize
                cms_PCA_SimpleOut(i) = (df_Tn(i) - df_TN(i)) / annuity(i);
           end
           
           out = cms_PCA_SimpleOut;
            
        end
        
         % Should check variance functions for HWHW later. 2020-02-18 by LIB
         function out =  CMS_PSA_SimpleDate(eqDuire_ck1f,valueDate,observeTime,numMatTime, tenor,modelStatesT)
           %CMT
%            tau = 0.25;
           tau = 1.0/(eqDuire_ck1f.freq);
            % if tenor is 0.25(3M) then use tenor(0.25) instead
           % model(zeroCurve)'s freq
           
           if abs(tenor- 0.25) < 1e-8
                tau = tenor;
           end
           
           to      = observeTime/365.0;
           toDate = valueDate.AddDate(observeTime,'day');
           tNDate = toDate.AddDate(tenor,'year');
           tN   =  tNDate.DateDiff(valueDate)/365.0;
           
           numMatDate = valueDate.AddDate(numMatTime,'day');
           
           p_nN = eqDuire_ck1f.PV01Date(valueDate,toDate,tNDate,tau);
           
           df_Tn = eqDuire_ck1f.DF(to);
           df_TN = eqDuire_ck1f.DF(tN);
           y_nN = (df_Tn - df_TN)/p_nN;
           
           c_nN = eqDuire_ck1f.C_nNDate(valueDate,toDate,tNDate,tau,p_nN,y_nN);
           g_nN = eqDuire_ck1f.G_nNDate(valueDate,toDate,tNDate,tau,p_nN);
%            h_nTerm = eqDuire_ck1f.H_nTermDate(valueDate,toDate,numMatDate);
           
           %h_nTerm is replace by i_Term & i_Tn_tilda in the following
           
           h_nTerm(1) = 0.0;
           
           varCovar = eqDuire_ck1f.LocalVariance(0,to);
           
           stateSize = size(modelStatesT,2);
           cms_PCA_SimpleOut = zeros(1,stateSize);
           
           driftTerm = 0;
           for i=1:1
               for j=1:1
                   driftTerm = driftTerm + (c_nN(i) * h_nTerm(j) + c_nN(i) * g_nN(j))*varCovar(i,j);
               end
           end
           
           % additional drift correction term from foreign Term USD to
           % domestic Term measure KRW
           i_Term = I_Term(eqDuire_ck1f,0,to,numMatTime/365.0);
           i_Tn_tilda = I_Tn_tilda(eqDuire_ck1f,0,to,to);
           j_x_tilda = J_x_tilda(eqDuire_ck1f,0,to,to);
           
%            additionalDrift = 0;
           additionalDrift = c_nN(1) * (i_Term + i_Tn_tilda + j_x_tilda);
           
           for i=1:stateSize
               cms_PCA_SimpleOut(i) = y_nN + driftTerm + additionalDrift + c_nN(1)*modelStatesT(1,i); 
           end
           
           out = cms_PCA_SimpleOut;
           
            
         end
         
%          function out = Foreign_HtT_r(eqDuire_ck1f,t,T)
%             out =  eqDuire_ck1f.H(T,eqDuire_ck1f.foreign_dH) - eqDuire_ck1f.H(t,eqDuire_ck1f.foreign_dH); 
%          end
%          
%          function out = Domestic_HtT_r(eqDuire_ck1f,t,T)
%             out =  eqDuire_ck1f.H(T,eqDuire_ck1f.domestic_dH) - eqDuire_ck1f.H(t,eqDuire_ck1f.domestic_dH); 
%          end
         
%          function out = H(eqDuire_ck1f,t,dH)
%             for i=1:length(dH.tenor)
%                 if t<= dH.tenor(i)
%                     break;
%                 end
%             end
%             tidx = i;
%             sum = 0.0;
%             prev_t = 0.0;
%             curr_t = 0.0;
%             for i=1:tidx
%                 if i< tidx
%                     curr_t = dH.tenor(i);
%                 else
%                     curr_t = t;
%                 end
%                 sum = sum + dH.quote(i)*(curr_t-prev_t);
% 
%                 prev_t = dH.tenor(i);
%             end
%             out = sum;
%          end

        function out = EQSpotMC(eqDupire_ck1f,valueDate,observeTime,numMatTime,irModelStatesT,eqModelStatesT)
        
            spotPrice = eqDupire_ck1f.spot.params('rawData');
            detFwd = eqDupire_ck1f.Fwd(spotPrice,observeTime); 
             
            meanR = eqDupire_ck1f.domestic_meanR_r;
            
             %stochasticFwd(0,T)
             
             stateSize = length(eqModelStatesT);
             stochasticFwd = zeros(stateSize,1);
             
             fwdVarianceEQOut = eqDupire_ck1f.FwdVarianceEQ(0,observeTime/365.0,numMatTime/365.0);
             for i=1:stateSize
                stochasticFwd(i) = detFwd * exp(eqModelStatesT(i) -1.0/meanR * irModelStatesT(i) -0.5*fwdVarianceEQOut);
%                 stochasticFwd(i) = detFwd * exp(eqModelStatesT(i) -0.5*fwdVarianceEQOut); 
             end
             
             out = stochasticFwd;
        
        end
        
        function out = FwdVarianceEQ(eqDuire_ck1f, from, to, Tnum)
            
            localVariance = zeros(3,1);
            measureChange = zeros(3,1);
            quantoChange = zeros(2,1);
            
            sigmaTimes = eqDuire_ck1f.domestic_vol_r.tenor;
            
            domestic_vol_r_Values = eqDuire_ck1f.domestic_vol_r.quote;
            meanR = eqDuire_ck1f.domestic_meanR_r;
            eqBlackVolValues =  eqDuire_ck1f.eqBlackVol.quote;
            
            correl_1 = ones(length(sigmaTimes),1);
            corr_dre_Values = eqDuire_ck1f.corr_dre.quote;
            
            localVariance(1) = eqDuire_ck1f.LocalVariance_Alpha2(from,to,sigmaTimes,eqBlackVolValues,eqBlackVolValues,correl_1);
            localVariance(2) = eqDuire_ck1f.GeneralVariance_BSHW(from,to,to,meanR,sigmaTimes,domestic_vol_r_Values,eqBlackVolValues,corr_dre_Values);
%             localVariance(3) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,to,to,meanR,meanR,sigmaTimes,domestic_vol_r_Values,domestic_vol_r_Values,correl_1);
            
%             quantoChange(1) = -1.0*eqDuire_ck1f.GeneralVariance_BSHW(from,to,T1,MRS_fr,sigmaTimes,foreign_vol_r_Values,fxValues,corr_frx_Values);
%             quantoChange(2) = -1.0*eqDuire_ck1f.GeneralVariance_BSHW(from,to,to,MRS_fr,sigmaTimes,foreign_vol_r_Values,fxValues,corr_frx_Values);
            
            measureChange(1) = eqDuire_ck1f.LocalVariance_HW_Alpha(from,to,to,meanR,sigmaTimes,domestic_vol_r_Values,eqBlackVolValues,corr_dre_Values);
%             measureChange(2) = eqDuire_ck1f.LocalVariance_HW_Alpha(from,to,to,meanR,sigmaTimes,domestic_vol_r_Values,domestic_vol_r_Values,correl_1);
            
%             measureChange(3) = eqDuire_ck1f.LocalVariance_HWHW(from,to,to,to,meanR,meanR,sigmaTimes,domestic_vol_r_Values,domestic_vol_r_Values,correl_1);
            
%             value = localVariance(1) + 2.0 * localVariance(2) + localVariance(3);
            value = localVariance(1) + 2.0 * localVariance(2);
            
            betaTerm = eqDuire_ck1f.Beta(to,Tnum);
            
%             value = value - 2.0 * -1.0 * betaTerm*(measureChange(1) + 1.0/meanR*(measureChange(2) - measureChange(3))); 
            value = value - 2.0 * -1.0 * betaTerm*(measureChange(1)); 
            
            out = value;
        
        end
        
        function out = fwdZcVarianceForeign(eqDuire_ck1f, from, to, T1, T2)
            localVariance = zeros(2,1);
            measureChange = zeros(2,1);
            quantoChange = zeros(2,1);
            
            sigmaTimes = eqDuire_ck1f.domestic_vol_r.tenor;
            
            domestic_vol_r_Values = eqDuire_ck1f.domestic_vol_r.quote;
            foreign_vol_r_Values = eqDuire_ck1f.foreign_vol_r.quote;
            
            fxValues = eqDuire_ck1f.fxBlackVol.quote;
            
            MRS_dr = eqDuire_ck1f.domestic_meanR_r;
            MRS_fr = eqDuire_ck1f.foreign_meanR_r;
            
            correl_1 = ones(length(sigmaTimes),1);
            corr_frx_Values = eqDuire_ck1f.corr_frx.quote;
            corr_drfr_Values = eqDuire_ck1f.corr_drfr.quote;
            
            localVariance(1) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,T1,T1,MRS_fr,MRS_fr,sigmaTimes,foreign_vol_r_Values,foreign_vol_r_Values,correl_1);
            localVariance(2) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,to,to,MRS_fr,MRS_fr,sigmaTimes,foreign_vol_r_Values,foreign_vol_r_Values,correl_1);
            
            quantoChange(1) = -1.0*eqDuire_ck1f.GeneralVariance_BSHW(from,to,T1,MRS_fr,sigmaTimes,foreign_vol_r_Values,fxValues,corr_frx_Values);
            quantoChange(2) = -1.0*eqDuire_ck1f.GeneralVariance_BSHW(from,to,to,MRS_fr,sigmaTimes,foreign_vol_r_Values,fxValues,corr_frx_Values);
            
            measureChange(1) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,T1,T2,MRS_fr,MRS_dr,sigmaTimes,foreign_vol_r_Values,domestic_vol_r_Values,corr_drfr_Values);
            measureChange(2) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,to,T2,MRS_fr,MRS_dr,sigmaTimes,foreign_vol_r_Values,domestic_vol_r_Values,corr_drfr_Values);
            
            value = localVariance(1) - localVariance(2);
            value = value - 2.0 * -1.0 * (quantoChange(1) - quantoChange(2));
            value = value - 2.0 * 1.0 * (measureChange(1) - measureChange(2));    
            
            out = value;
            
        end
        
        function beta = Beta(eqDuire_ck1f, t, T)
            a_r = eqDuire_ck1f.domestic_meanR_r;
            beta =[];
            
            if(abs(a_r) > 1.0E-12)
                beta(1) = (1.0 - exp(-a_r * (T - t))) / a_r;
            else
                beta(1) = (T - t);
            end
            
        end
        
        function beta = BetaDate(eqDuire_ck1f, valueDate, tDate, TDate)
            t = tDate.DateDiff(valueDate) / 365.0;
            T = TDate.DateDiff(valueDate) / 365.0;
            
            a_r = eqDuire_ck1f.foreign_meanR_r;
            beta =[];
            
            if(abs(a_r) > 1.0E-12)
                beta(1) = (1.0 - exp(-a_r * (T - t))) / a_r;
            else
                beta(1) = (T-t);
            end
            
        end
        
        function c_nN = C_nN(eqDuire_ck1f, tn, tN, tau, pnN, ynN)
            p = @eqDuire_ck1f.DF;
            c_nN = [0.0];
            
            for i = 1:round((tN - tn) / tau)
                tp = tn + i * tau;
                beta = eqDuire_ck1f.Beta(tn, tp);
                df = p(tp);
                c_nN(1) = c_nN(1) +tau * beta(1) * df;
            end
            
            c_nN(1) = c_nN(1) * ynN;
            c_nN(1) = c_nN(1) + beta(1) * df;
            c_nN(1) = c_nN(1) / pnN;
            
        end
        
        function c_nN = C_nNDate(eqDuire_ck1f,valueDate,tnDate,tNDate,tau,pnN,ynN)
            tn = tnDate.DateDiff(valueDate) / 365.0;
            tN = tNDate.DateDiff(valueDate) / 365.0;
            
            addMonthUnit = round(12*tau);
            cnt = round((tN-tn)/tau);
            
            p = @eqDuire_ck1f.DF;
            c_nN=[0.0];
            beta = [0.0];
            df = 0.0;
            prevTime = tn;
            deltaT = 0.0;
            for i=1:cnt
                tpDate = tnDate.AddDate(i*addMonthUnit,'month');
                tp = tpDate.DateDiff(valueDate)/365.0;
                deltaT = tp - prevTime;
                beta = eqDuire_ck1f.BetaDate(valueDate,tnDate,tpDate);
                df = p(tp);
%                 c_nN(1) = c_nN(1) +tau * beta(1) * df;
                c_nN(1) = c_nN(1) +deltaT * beta(1) * df;
                prevTime = tp;
            end
            
            c_nN(1) = c_nN(1)* ynN;
            
            c_nN(1) = c_nN(1) + beta(1)*df;
            
            c_nN(1) = c_nN(1)/pnN;
        end
        
        function g_nN = G_nN(eqDuire_ck1f,tn,tN,tau,pnN)
            p = @eqDuire_ck1f.DF;
            g_nN=[0.0];
            
            for i=1:round((tN-tn)/tau)
                tp = tn+i*tau;
                beta = eqDuire_ck1f.Beta(tn,tp);
                df = p(tp);
                g_nN(1) = g_nN(1) +tau * beta(1) * df;
            end
            
            g_nN(1) = g_nN(1)/pnN;
        end
        
        function g_nN = G_nNDate(eqDuire_ck1f,valueDate,tnDate,tNDate,tau,pnN)
            tn = tnDate.DateDiff(valueDate)/365.0;
            tN = tNDate.DateDiff(valueDate)/365.0;
            addMonthUnit = round(12*tau);
            cnt = round((tN-tn)/tau);
            
            p = @eqDuire_ck1f.DF;
            g_nN=[0.0];
            
            prevTime = tn;
            deltaT = 0.0;
            for i=1:cnt
                tpDate = tnDate.AddDate(i*addMonthUnit,'month');
                tp = tpDate.DateDiff(valueDate)/365.0;
                deltaT = tp - prevTime;
                beta = eqDuire_ck1f.BetaDate(valueDate,tnDate,tpDate);
                df = p(tp);
%                 g_nN(1) = g_nN(1) +tau * beta(1) * df;
                g_nN(1) = g_nN(1) + deltaT * beta(1) * df;
                prevTime = tp;
            end
            
            g_nN(1) = g_nN(1)/pnN;
        end
        
        function h_nTerm = H_nTerm(eqDuire_ck1f,tn,tTerm)
           h_nTerm =[];
           beta = eqDuire_ck1f.Beta(tn,tTerm);
           h_nTerm(1) = -1.0*beta(1);
        end
        
        function h_nTerm = H_nTermDate(eqDuire_ck1f,valueDate,tnDate,tTermDate)
           h_nTerm =[];
           beta = eqDuire_ck1f.BetaDate(valueDate,tnDate,tTermDate);
           h_nTerm(1) = -1.0*beta(1);
        end
        
        function i_Term = I_Term(eqDuire_ck1f,from,to,tTerm)

            fMRS = eqDuire_ck1f.foreign_meanR_r;
            sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
            foreign_vol_r_Values = eqDuire_ck1f.foreign_vol_r.quote;
            
            dMRS = eqDuire_ck1f.domestic_meanR_r;
            domestic_vol_r_Values = eqDuire_ck1f.domestic_vol_r.quote;
            
            corr_drfr_Values = eqDuire_ck1f.corr_drfr.quote;
                        
            % QuantoCK1F_LGM2F case
%             variance_drfr = eqDuire_ck1f.GeneralVariance_HWLGM_type2(from,to,to,tTerm,MRS1,sigmaTimes,domestic_dH_r_Values,domestic_Alpha_r_Values,...
%                                                          foreign_vol_r_Values,corr_drfr_Values);
            
            % eqDuire_ck1f case
            variance_drfr = eqDuire_ck1f.GeneralVariance_HWHW_type2(from, to, to, tTerm, dMRS, fMRS, sigmaTimes,...
                                                            domestic_vol_r_Values, foreign_vol_r_Values, corr_drfr_Values);
            
            % we add minus 1 so that we don't need additional minus in
            % drift adjust term
            i_Term = -1.0 * (variance_drfr);
           
        end
        
        function i_Tn_tilda = I_Tn_tilda(eqDuire_ck1f,from,to,tn)

            MRS1 = eqDuire_ck1f.foreign_meanR_r;
            sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
            foreign_vol_r_Values = eqDuire_ck1f.foreign_vol_r.quote;
            corr_frfr_Values = ones(length(sigmaTimes),1);
            
            variance_frfr = eqDuire_ck1f.GeneralVariance_HWHW_type2(from,to,tn,tn,MRS1,MRS1,sigmaTimes,...
                                                                        foreign_vol_r_Values,foreign_vol_r_Values,corr_frfr_Values);
           % we don't need minus 1
           i_Tn_tilda = 1.0 * variance_frfr;
           
        end
        
%         function i_Tn_tilda = I_Tn_tilda_old(eqDuire_ck1f,from,to,tn)
% 
%             sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
%             sigmaSize =  length(sigmaTimes);
%             
%             for i=1:sigmaSize
%                 if from<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             startIdx = i;
%             
%             for i=1:sigmaSize
%                 if to<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             endIdx = i;
%            
%            MRS2 = eqDuire_ck1f.foreign_meanR_r;
%            
%            newExpScale = zeros(2,1);
%            lastExpScale = zeros(2,1);
%            variances = zeros(2,1);
%             
%            lastU  = from;
%            
%            lastExpScale(1) = exp(MRS2*lastU);
%            lastExpScale(2) = exp((MRS2 + MRS2)*lastU);
%            
%            sigmaValues1 = eqDuire_ck1f.foreign_vol_r.quote;
%            sigmaValues2 = eqDuire_ck1f.foreign_vol_r.quote;
%            corr12 = 1.0;
% 
%            
%            for i=startIdx:endIdx
%                 if (i< endIdx) U = sigmaTimes(i);else U = to;end;
%                 if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
%                 if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
%                 
%                 newExpScale(1) = exp(MRS2*U);
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(1)-lastExpScale(1));
%                 lastExpScale(1) = newExpScale(1);
%                 
%                 newExpScale(2) = exp((MRS2+MRS2)*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/(MRS2+MRS2)) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
%                 
%                 lastU = U;
%            end
%            
%            value = exp(-1.0*MRS2*tn)*(1.0/ MRS2)*variances(1);
%            value = value + -1.0*exp(-1.0*(MRS2 + MRS2)*tn)*(1.0/ MRS2)*variances(2);
%            % we don't need minus 1
%            i_Tn_tilda = 1.0 * value;
%            
%         end
        
        
        
        function j_x_tilda = J_x_tilda(eqDuire_ck1f,from,to,tn)

            MRS1 = eqDuire_ck1f.foreign_meanR_r;
            sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
            foreign_vol_r_Values = eqDuire_ck1f.foreign_vol_r.quote;
            fxBlackVol_Values = eqDuire_ck1f.fxBlackVol.quote;
            corr_frx_Values = eqDuire_ck1f.corr_frx.quote;
            
            variance_frx = eqDuire_ck1f.GeneralVariance_BSHW_type2(from,to,tn,MRS1,sigmaTimes,...
                                                                        foreign_vol_r_Values,fxBlackVol_Values,corr_frx_Values);
           
           % we need minus 1
           j_x_tilda = -1.0 * variance_frx;
           
        end
        
%         function j_x_tilda = J_x_tilda_old(eqDuire_ck1f,from,to,tn)
% 
%             sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
%             sigmaSize =  length(sigmaTimes);
%             
%             for i=1:sigmaSize
%                 if from<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             startIdx = i;
%             
%             for i=1:sigmaSize
%                 if to<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             endIdx = i;
%            
%             
%            newExpScale = zeros(1,1);
%            lastExpScale = zeros(1,1);
%            
%            lastU  = from;
%            MRS2 = eqDuire_ck1f.foreign_meanR_r;
%            lastExpScale(1) = exp(MRS2*lastU);
%            variances = 0.0;
%            
%            sigmaValues1 = eqDuire_ck1f.fxBlackVol.quote;
%            sigmaValues2 = eqDuire_ck1f.foreign_vol_r.quote;
%            corrValues12 = eqDuire_ck1f.corr_frx.quote;
%            
%            for i=startIdx:endIdx
%                 if (i< endIdx) U = sigmaTimes(i);else U = to;end;
%                 if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
%                 if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
%                 if (i< sigmaSize) corr12 = corrValues12(i);else corr12 = corrValues12(sigmaSize);end;
%                 
%                 newExpScale(1) = exp(MRS2*U);
%                 variances = variances + corr12 * vol1 * vol2 * (1.0/MRS2) * (newExpScale(1)-lastExpScale(1));
%                 lastExpScale(1) = newExpScale(1);
%                 
%                 lastU = U;
%            end
%            
%            % we need minus 1
%            j_x_tilda = -1.0 * exp(-1.0*MRS2*tn) * (1.0/MRS2) * variances;
%            
%         end
        
        function out = discountFactor(eqDuire_ck1f, startTime, endTime, numMatTime, modelStatesT) 
           zcT = eqDuire_ck1f.DF(endTime/365.0);
           
           %numOfPath
           stateSize = size(modelStatesT, 2);
           discountFactorOut = zeros(1, stateSize);
           
           % deterministic discount factor
           if startTime <= 1e-8
               for i = 1:stateSize
                   discountFactorOut(i) = zcT;
               end
                
               out = discountFactorOut;
               return;
           end
           
           % deterministic discount factor or maturity in the past
           if startTime >= endTime
               out = ones(1,stateSize);
               return;
           end
           
           zct = eqDuire_ck1f.DF(startTime / 365.0);
           beta = eqDuire_ck1f.Beta(startTime/365.0, endTime/365.0);
           zcDriftTerm = eqDuire_ck1f.fwdZcVarianceForeign(0, startTime/365.0, endTime/365.0, numMatTime/365.0);
           
           % eqDuire_ck1f is one factor model
           for i = 1:stateSize
%                discountFactorOut(i) = zcT/zct * exp(-0.5*zcDriftTerm - beta(1)*modelStatesT(1,i));
               discountFactorOut(i) = zcT / zct * exp(-0.5 * zcDriftTerm - beta(1) * modelStatesT(1, i));
           end
           
           out = discountFactorOut;
           
        end
        
%         function out = discountPayoff(eqDuire_ck1f,eventTime,numMatTime ...
%                 ,modelStatesT,cashflow)
%             
%             dfNumMat = eqDuire_ck1f.GetChildModel('d').DF(numMatTime/365.0);
%             % for discountPayoff T=numMatTime
%             % P(0,TnumMat)/P(Te,Tnummat)*Payoff
%             %
%             domesticModelStatesT = modelStatesT(1,:);
%             discountT = eqDuire_ck1f.GetChildModel('d').discountFactor(eventTime, numMatTime,numMatTime,domesticModelStatesT);
%             stateSize = size(modelStatesT,2);
%             payoff = zeros(1,stateSize);
%             for i=1:stateSize
%                 payoff(i)= dfNumMat/discountT(i)*cashflow(i);
%             end    
%             out = payoff;
%         end
        
        function variances = LocalVariance(eqDuire_ck1f,from,to)

            sig(1) = eqDuire_ck1f.foreign_vol_r;
            meanR(1) = eqDuire_ck1f.foreign_meanR_r;
            
            alphaSize = length(sig(1).quote);
            
            for i=1:length(sig(1).tenor)
                if from<= sig(1).tenor(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sig(1).tenor)
                if to<= sig(1).tenor(i)
                    break;
                end
            end
            endIdx = i;
            
            tiny = zeros(1,1);
            lastExpScale = zeros(1,1);
            newExpScale  = zeros(1,1);
            
            for i=1:1
                for j=1:1
                    if(abs(meanR(i)+meanR(j)) < 1.0E-12) tiny(i,j) = 1; else tiny(i,j) = 0; end
                    lastExpScale(i,j) =  exp((meanR(i)+meanR(j))*from);
                end
            end
  
           lastU  = from;
           
           variances = zeros(1,1);
           
           for i=startIdx:endIdx
                if (i< endIdx) U = sig(1).tenor(i);else U = to;end;
                if (i< alphaSize) vol(1) = sig(1).quote(i);else vol(1) = sig(1).quote(alphaSize);end;
                
                correl =ones(1,1);
                for j=1:1
                    for k=1:1
                        newExpScale(j,k) =  exp((meanR(j)+meanR(k))*U);
                        if(tiny(j,k)~=1)
                            scale =newExpScale(j,k)-lastExpScale(j,k);
                        else
                            scale = U - lastU;
                        end
                        variances(j,k) = variances(j,k) + vol(j)*vol(k)*correl(j,k)...
                                       * scale;
                        lastExpScale(j,k) = newExpScale(j,k);
                    end
                end
                lastU = U;
           end
           
           for j=1:1
                for k=1:1
                    if(tiny(j,k)~= 1)
                        variances(j,k) = variances(j,k)/(meanR(j)+meanR(k))*exp(-1.0*(meanR(j)+meanR(k))*to);
                    end
                end
           end
           
        end
        
        function out = LocalDrift(eqDuire_ck1f,from,to)
            drift = eye(2,2);
            drift(1,1) = exp(-1.0*eqDuire_ck1f.domestic_meanR_r*(to-from));
            drift(2,2) = 1.0;
            out = drift;
        end
        
        function variances = LocalCovariance(eqDuire_ck1f,from,to)

            % Covariance Between,
            % X(t) ~ int{from,to}_{exp(-a*(to-u))*sigma_d(u)*dW_d(u)} &
            % Z(t) ~ int{from,to}_{sigma_e(u)*dW_e(u)-1/a*sigma_d(u)*dW_d(u)}

            sigmaValue1 = eqDuire_ck1f.domestic_vol_r.quote;
            sigmaValue2 = eqDuire_ck1f.eqBlackVol.quote;
            
            corr12 = eqDuire_ck1f.corr_dre.quote;
            meanR = eqDuire_ck1f.domestic_meanR_r;
            sigmaTimes = eqDuire_ck1f.domestic_vol_r.tenor;
            corr11 = 1.0*ones(length(sigmaTimes),1);
            
            variances = zeros(2, 2);
            
            variances(1,1) = eqDuire_ck1f.LocalVariance_HWHW(from,to,to,to,meanR,meanR,sigmaTimes,sigmaValue1,sigmaValue1,corr11);
            
            
            variances12 = eqDuire_ck1f.LocalVariance_HW_Alpha(from,to,to,meanR,sigmaTimes,sigmaValue1,sigmaValue2,corr12);
            variances12 = variances12 +1.0/meanR*eqDuire_ck1f.LocalVariance_HW_Alpha(from,to,to,meanR,sigmaTimes,sigmaValue1,sigmaValue1,corr11);
            variances(1,2) = variances12;
            
            variances(2,1) = variances(1,2);
            
            variance22 = eqDuire_ck1f.LocalVariance_Alpha2(from,to,sigmaTimes,sigmaValue2,sigmaValue2,corr11);
            variance22 = variance22 +     2.0*1.0/meanR*eqDuire_ck1f.LocalVariance_Alpha2(from,to,sigmaTimes,sigmaValue1,sigmaValue2,corr12);
            variance22 = variance22 +1.0/meanR*1.0/meanR*eqDuire_ck1f.LocalVariance_Alpha2(from,to,sigmaTimes,sigmaValue1,sigmaValue1,corr11);
            
            variances(2,2) = variance22;
           
            
        end
        
        function out = LocalVariance_HW_Alpha(eqDuire_ck1f,from,to,T1,MRS1,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [from,to] of e^{-a(T1-s)}*sigma1(s)sigma2(s)
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(4,1);
            lastExpScale = zeros(4,1);
            variances = zeros(4,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS1*lastU);
%             lastExpScale(3) = exp(MRS2*lastU);
%             lastExpScale(4) = exp((MRS1 + MRS2)*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end;
                
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
                newExpScale(2) = exp(MRS1*U);
                variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
                lastExpScale(2) = newExpScale(2);
                
%                 newExpScale(3) = exp(MRS2*U);
%                 variances(3) = variances(3) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(3)-lastExpScale(3));
%                 lastExpScale(3) = newExpScale(3);
%                 
%                 newExpScale(4) = exp((MRS1+MRS2)*U);
%                 variances(4) = variances(4) + corr12 * sig1 * sig2 * (1.0/(MRS1+MRS2)) * (newExpScale(4)-lastExpScale(4));
%                 lastExpScale(4) = newExpScale(4);
                
                lastU = U;
                
            end
            
%             value = (1.0/ MRS1)*(1.0/MRS2)*variances(1);
%             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*(1.0/MRS2)*variances(2);
%             value = value + -1.0*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(3);
%             value = value +  1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(4);

%             value = 1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*variances(2);
            
            value = 1.0*exp(-1.0*MRS1*T1)*variances(2);
            out  = value;
        end
        
        function out = LocalVariance_HWHW(eqDuire_ck1f,from,to,T1,T2,MRS1,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)

            % Variance in [from,to] of
            % e^{-a(T1-s)}*e^{-b(T2-s)}*sigma1(s)*sigma2(s)*corr12(s)
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(4,1);
            lastExpScale = zeros(4,1);
            variances = zeros(4,1);
            
            lastU  = from;
%             lastExpScale(2) = exp(MRS1*lastU);
%             lastExpScale(3) = exp(MRS2*lastU);
            lastExpScale(4) = exp((MRS1 + MRS2)*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end;
                
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
%                 
%                 newExpScale(2) = exp(MRS1*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
%                 
%                 newExpScale(3) = exp(MRS2*U);
%                 variances(3) = variances(3) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(3)-lastExpScale(3));
%                 lastExpScale(3) = newExpScale(3);
%                 
                newExpScale(4) = exp((MRS1+MRS2)*U);
                variances(4) = variances(4) + corr12 * sig1 * sig2 * (1.0/(MRS1+MRS2)) * (newExpScale(4)-lastExpScale(4));
                lastExpScale(4) = newExpScale(4);
                
                lastU = U;
                
            end
            
%             value = (1.0/ MRS1)*(1.0/MRS2)*variances(1);
%             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*(1.0/MRS2)*variances(2);
%             value = value + -1.0*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(3);
%             value = 1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(4);
            value = 1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*variances(4);

            out  = value;
        end
        
        function out = LocalVariance_H2_Alpha2(eqDuire_ck1f,from,to,sigmaTimes,dH1Values, dH2Values, sigmaValues1,sigmaValues2,corrValues)

            sigmaSize =  length(sigmaTimes);
            
            for i=1:sigmaSize
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:sigmaSize
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
  
           lastU  = from;
           
           variances = 0.0;
           
           dH1.quote = dH1Values;
           dH1.tenor = sigmaTimes;
           
           dH2.quote = dH2Values;
           dH2.tenor = sigmaTimes;
           
           for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
                if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
                if (i< sigmaSize) dH1Value = dH1.quote(i);else dH1Value = dH1.quote(sigmaSize);end;
                if (i< sigmaSize) dH2Value = dH2.quote(i);else dH2Value = dH2.quote(sigmaSize);end;
                if (i< sigmaSize) correl = corrValues(i);else correl = corrValues(sigmaSize);end;
                
                variances = variances + eqDuire_ck1f.H(lastU,dH1)*eqDuire_ck1f.H(lastU,dH2)*correl*vol1*vol2*(U - lastU);
                variances = variances + dH1Value*eqDuire_ck1f.H(lastU,dH2)*correl*vol1*vol2*0.5*(U - lastU)*(U - lastU);
                variances = variances + eqDuire_ck1f.H(lastU,dH1)*dH2Value*correl*vol1*vol2*0.5*(U - lastU)*(U - lastU);
                variances = variances + dH1Value*dH2Value*correl*vol1*vol2*1.0/3.0*(U - lastU)*(U - lastU)*(U - lastU);
                
                
                lastU = U;
           end
           
           out = variances;
           
        end
        
        function out = LocalVariance_H_Alpha2(eqDuire_ck1f,from,to,sigmaTimes,dH1Values,sigmaValues1,sigmaValues2,corrValues)

            sigmaSize =  length(sigmaTimes);
            
            for i=1:sigmaSize
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:sigmaSize
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
  
           lastU  = from;
           
           variances = 0.0;
           
           dH1.quote = dH1Values;
           dH1.tenor = sigmaTimes;
           
           for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
                if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
                if (i< sigmaSize) dH = dH1.quote(i);else dH = dH1.quote(sigmaSize);end;
                if (i< sigmaSize) correl = corrValues(i);else correl = corrValues(sigmaSize);end;
                
                variances = variances + eqDuire_ck1f.H(lastU,dH1) * correl * vol1 * vol2 * (U - lastU);
                variances = variances + 0.5 * dH * correl * vol1 * vol2 * (U - lastU) * (U - lastU);
                lastU = U;
           end
           
           out = variances;
           
        end
        
        function out = LocalVariance_Alpha2(eqDuire_ck1f,from,to,sigmaTimes,sigmaValues1,sigmaValues2,corrValues)

            sigmaSize =  length(sigmaTimes);
            
            for i=1:sigmaSize
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:sigmaSize
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
  
           lastU  = from;
           
           variances = 0.0;
           
           for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
                if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
                if (i< sigmaSize) correl = corrValues(i);else correl = corrValues(sigmaSize);end;
                
                variances = variances + correl* vol1 * vol2 * (U - lastU);
                lastU = U;
           end
           
           out = variances;
           
        end
        
        function out = GeneralVariance_HWHW(eqDuire_ck1f,from,to,T1,T2,MRS1,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [from,to] of 1/a*(1-e^{-a(T1-s)})*1/b*(1-e^{-b(T2-s)})sigma1(s)sigma2(s)
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(4,1);
            lastExpScale = zeros(4,1);
            variances = zeros(4,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS1*lastU);
            lastExpScale(3) = exp(MRS2*lastU);
            lastExpScale(4) = exp((MRS1 + MRS2)*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end;
                
                variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
                newExpScale(2) = exp(MRS1*U);
                variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
                lastExpScale(2) = newExpScale(2);
                
                newExpScale(3) = exp(MRS2*U);
                variances(3) = variances(3) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(3)-lastExpScale(3));
                lastExpScale(3) = newExpScale(3);
                
                newExpScale(4) = exp((MRS1+MRS2)*U);
                variances(4) = variances(4) + corr12 * sig1 * sig2 * (1.0/(MRS1+MRS2)) * (newExpScale(4)-lastExpScale(4));
                lastExpScale(4) = newExpScale(4);
                
                lastU = U;
                
            end
            
            value = (1.0/ MRS1)*(1.0/MRS2)*variances(1);
            value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*(1.0/MRS2)*variances(2);
            value = value + -1.0*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(3);
            value = value +  1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(4);

            out  = value;
        end
        
        function out = GeneralVariance_HWHW_type2(eqDuire_ck1f,from,to,T1,T2,MRS1,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [a,b] of 1/a*(1-e^{-a(T1-s)})*e^{-b(T2-s)}*sigma1(s)sigma2(s)
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(4,1);
            lastExpScale = zeros(4,1);
            variances = zeros(4,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS1*lastU);
            lastExpScale(3) = exp(MRS2*lastU);
            lastExpScale(4) = exp((MRS1 + MRS2)*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end;
                
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
%                 newExpScale(2) = exp(MRS1*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
                
                newExpScale(3) = exp(MRS2*U);
                variances(3) = variances(3) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(3)-lastExpScale(3));
                lastExpScale(3) = newExpScale(3);
                
                newExpScale(4) = exp((MRS1+MRS2)*U);
                variances(4) = variances(4) + corr12 * sig1 * sig2 * (1.0/(MRS1+MRS2)) * (newExpScale(4)-lastExpScale(4));
                lastExpScale(4) = newExpScale(4);
                
                lastU = U;
                
            end
            
%             value = (1.0/ MRS1)*(1.0/MRS2)*variances(1);
%             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*(1.0/MRS2)*variances(2);
            value =  +1.0*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*variances(3);
            value = value +  -1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*variances(4);

            out  = value;
        end
        
%         function out = GeneralVariance_HWLGM(eqDuire_ck1f,from,to,T1,T2,MRS1,sigmaTimes,dH1Values,sigmaValue1,sigmaValue2,corrValue)
%             % Variance in [from,to] of 1/a*(1-e^{-a(T1-s)})*(H(T2)-H(s))*sigma1(s)sigma2(s)
%             
%             dH1.quote = dH1Values;
%             dH1.tenor = sigmaTimes;
%             
%             sigmaSize = length(sigmaValue1);
%             
%             for i=1:length(sigmaTimes)
%                 if from<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             startIdx = i;
%             
%             for i=1:length(sigmaTimes)
%                 if to<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             endIdx = i;
%             
%             
%             newExpScale = zeros(4,1);
%             lastExpScale = zeros(4,1);
%             variances = zeros(4,1);
%             
%             lastU  = from;
%             lastExpScale(2) = exp(MRS1*lastU);
%             lastExpScale(3) = exp(MRS1*lastU);
%             lastExpScale(4) = exp(MRS1*lastU);
%             
%             for i=startIdx:endIdx
%                 if (i< endIdx) U = sigmaTimes(i);else U = to;end
%                 if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end
%                 if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end
%                 if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end
%                 if (i< sigmaSize) dH = dH1Values(i);else dH = dH1Values(sigmaSize);end
%                 
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
%                 
%                 newExpScale(2) = exp(MRS1*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
%                 
%                 newExpScale(3) = exp(MRS1*U);
%                 variances(3) = variances(3) + eqDuire_ck1f.H(lastU,dH1) * corr12 * sig1 * sig2 * (U - lastU);
%                 variances(3) = variances(3) + dH * corr12 * sig1 * sig2 * 0.5 * (U - lastU) * (U - lastU);
%                 lastExpScale(3) = newExpScale(3);
%                 
%                 newExpScale(4) = exp(MRS1*U);
%                 variances(4) = variances(4) + eqDuire_ck1f.H(lastU,dH1) * corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(4)-lastExpScale(4));
%                 variances(4) = variances(4) + dH * corr12 * sig1 * sig2 * (1.0/MRS1) * (U*newExpScale(4)-lastU*lastExpScale(4));
%                 variances(4) = variances(4) -1.0*dH * corr12 * sig1 * sig2 * (1.0/MRS1) * (1.0/MRS1) * (newExpScale(4)-lastExpScale(4));
%                 variances(4) = variances(4) -1.0*dH * corr12 * sig1 * sig2 * (1.0/MRS1) * lastU * (newExpScale(4)-lastExpScale(4));
%                 lastExpScale(4) = newExpScale(4);
%                 
%                 lastU = U;
%                 
%             end
%             
%             value = eqDuire_ck1f.H(T2,dH1)*(1.0/MRS1)*variances(1);
%             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/MRS1)*eqDuire_ck1f.H(T2,dH1)*variances(2);
%             value = value + -1.0*(1.0/MRS1)*variances(3);
%             value = value +  1.0*exp(-1.0*MRS1*T1)*(1.0/MRS1)*variances(4);
% 
%             out  = value;
%         end
        
%         function out = GeneralVariance_HWLGM_type2(eqDuire_ck1f,from,to,T1,T2,MRS1,sigmaTimes,dH1Values,sigmaValue1,sigmaValue2,corrValue)
%         % Variance in [a,b] of e^{-a(T1-s)}*(H(T2)-H(s))*sigma1(s)sigma2(s)
%             
%             dH1.quote = dH1Values;
%             dH1.tenor = sigmaTimes;
%             
%             sigmaSize = length(sigmaValue1);
%             
%             for i=1:length(sigmaTimes)
%                 if from<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             startIdx = i;
%             
%             for i=1:length(sigmaTimes)
%                 if to<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             endIdx = i;
%             
%             
%             newExpScale = zeros(4,1);
%             lastExpScale = zeros(4,1);
%             variances = zeros(4,1);
%             
%             lastU  = from;
%             lastExpScale(2) = exp(MRS1*lastU);
%             lastExpScale(3) = exp(MRS1*lastU);
%             lastExpScale(4) = exp(MRS1*lastU);
%             
%             for i=startIdx:endIdx
%                 if (i< endIdx) U = sigmaTimes(i);else U = to;end
%                 if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end
%                 if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end
%                 if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end
%                 if (i< sigmaSize) dH = dH1Values(i);else dH = dH1Values(sigmaSize);end
%                 
% %                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
%                 
%                 newExpScale(2) = exp(MRS1*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
%                 
% %                 newExpScale(3) = exp(MRS1*U);
% %                 variances(3) = variances(3) + eqDuire_ck1f.H(lastU,dH1) * corr12 * sig1 * sig2 * (U - lastU);
% %                 variances(3) = variances(3) + dH * corr12 * sig1 * sig2 * 0.5 * (U - lastU) * (U - lastU);
% %                 lastExpScale(3) = newExpScale(3);
%                 
%                 newExpScale(4) = exp(MRS1*U);
%                 variances(4) = variances(4) + eqDuire_ck1f.H(lastU,dH1) * corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(4)-lastExpScale(4));
%                 variances(4) = variances(4) + dH * corr12 * sig1 * sig2 * (1.0/MRS1) * (U*newExpScale(4)-lastU*lastExpScale(4));
%                 variances(4) = variances(4) -1.0*dH * corr12 * sig1 * sig2 * (1.0/MRS1) * (1.0/MRS1) * (newExpScale(4)-lastExpScale(4));
%                 variances(4) = variances(4) -1.0*dH * corr12 * sig1 * sig2 * (1.0/MRS1) * lastU * (newExpScale(4)-lastExpScale(4));
%                 lastExpScale(4) = newExpScale(4);
%                 
%                 lastU = U;
%                 
%             end
%             
% %             value = eqDuire_ck1f.H(T2,dH1)*(1.0/MRS1)*variances(1);
% %             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/MRS1)*eqDuire_ck1f.H(T2,dH1)*variances(2);
%             value = +1.0*exp(-1.0*MRS1*T1)*eqDuire_ck1f.H(T2,dH1)*variances(2);
%             
% %             value = value + -1.0*(1.0/MRS1)*variances(3);
%             value = value +  -1.0*exp(-1.0*MRS1*T1)*variances(4);
% 
%             out  = value;
%         end
        
        function out = GeneralVariance_BSHW(eqDuire_ck1f,from,to,T2,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [from,to] of 1/a*(1-e^{-a(T1-s)})sigma1(s)sigma2(s)
            
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(2,1);
            lastExpScale = zeros(2,1);
            variances = zeros(2,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS2*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end
                
                variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
                newExpScale(2) = exp(MRS2*U);
                variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(2)-lastExpScale(2));
                lastExpScale(2) = newExpScale(2);
                
                lastU = U;
                
            end
            
            value = (1.0/MRS2)*variances(1);
            value = value + -1.0*exp(-1.0*MRS2*T2)*(1.0/MRS2)*variances(2);
            
            out  = value;
        end
        
        function out = GeneralVariance_BSHW_type2(eqDuire_ck1f,from,to,T2,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [a,b] of (e^{-a(T1-s)})sigma1(s)sigma2(s)
            
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(2,1);
            lastExpScale = zeros(2,1);
            variances = zeros(2,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS2*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end
                
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
                newExpScale(2) = exp(MRS2*U);
                variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(2)-lastExpScale(2));
                lastExpScale(2) = newExpScale(2);
                
                lastU = U;
                
            end
            
%             value = (1.0/MRS2)*variances(1);
            value = +1.0*exp(-1.0*MRS2*T2)*variances(2);
            
            out  = value;
        end
        
        function out = CMSDigitalArgDate(eqDuire_ck1f,valueDate,toDate,tpDate,tenor1,tau)
           % probability that CMS rate > strike
            %CMS 1
           to = toDate.DateDiff(valueDate)/365.0;
           if tenor1 < 1 && tenor1 >= 1.0/12.0
               tenorMonth = round(12*tenor1);
                tN1Date = toDate.AddDate(tenorMonth,'month');
           elseif tenor1 >= 1
               tN1Date = toDate.AddDate(tenor1,'year');
           else
               disp('unimplemented')
           end
           
           tN1   =  tN1Date.DateDiff(valueDate)/365.0;
           
           % if tenor is 0.25(3M) then use tenor(0.25) instead
           % model(zeroCurve)'s freq
           tauIn = tau;
           if abs(tenor1- 0.25) < 1e-8
                tauIn = tenor1;
           end
           
           p_nN1 = eqDuire_ck1f.PV01Date(valueDate,toDate,tN1Date,tauIn);
           
           df_Tn1 = eqDuire_ck1f.DF(to);
           df_TN1 = eqDuire_ck1f.DF(tN1);
           y_nN1 = (df_Tn1 - df_TN1)/p_nN1;
           
           c_nN1 = eqDuire_ck1f.C_nNDate(valueDate,toDate,tN1Date,tauIn,p_nN1,y_nN1);
           g_nN1 = eqDuire_ck1f.G_nNDate(valueDate,toDate,tN1Date,tauIn,p_nN1);
%            h_nTerm1 = eqDuire_ck1f.H_nTermDate(valueDate,toDate,tpDate);
           % h_nTerm1 is replaced with i_Term & i_Tn_tilda as in the
           % following discussion
           
           h_nTerm1(1) = 0.0;
           
           varCovar = eqDuire_ck1f.LocalVariance(0,to);
           
           driftTerm=0.0;
           for i=1:1
               for j=1:1
                    driftTerm = driftTerm + c_nN1(i) * (h_nTerm1(j) + g_nN1(j)) * varCovar(i,j);
               end
           end
           
           tpTime = tpDate.DateDiff(valueDate);
           % additional drift correction term from foreign Term measure USD to KRW domestic Term 
           i_Term = I_Term(eqDuire_ck1f,0,to,tpTime/365.0);
           i_Tn_tilda = I_Tn_tilda(eqDuire_ck1f,0,to,to);
           j_x_tilda = J_x_tilda(eqDuire_ck1f,0,to,to);
           
%            additionalDrift = 0;
           additionalDrift = c_nN1(1) *(i_Term + i_Tn_tilda + j_x_tilda);
           
           variance = 0.0;
           for i=1:1
               for j=1:1
                    variance = variance + c_nN1(i) * c_nN1(j) * varCovar(i,j);
               end
           end
           
           out.fwdCMS = y_nN1;
           out.mu = y_nN1 + driftTerm + additionalDrift;
           out.sigma = sqrt(variance);
           out.c_nN = c_nN1;
           out.varCovar = varCovar;
        end
        
        function out = computeBSCK1FCK1FVariance(eqDuire_ck1f,a,b,T,corr_drfr,corr_drx,corr_frx,...
                                  fxBlackVol, domestic_meanR_r, domestic_vol_r,...
                                  foreign_meanR_r, foreign_vol_r)
          % synchronize model parameters time-steps start 
            corr_drfr_Tenor = corr_drfr.tenor;
            corr_drfr_Quote = corr_drfr.quote;
            
            corr_drx_Tenor = corr_drx.tenor;
            corr_drx_Quote = corr_drx.quote;
            
            corr_frx_Tenor = corr_frx.tenor;
            corr_frx_Quote = corr_frx.quote;
            
            fxBlackVolTenor = fxBlackVol.tenor;
            fxBlackVolQuote = fxBlackVol.quote;

            domestic_vol_r_Tenor = domestic_vol_r.tenor;
            domestic_vol_r_Quote = domestic_vol_r.quote;
            
            foreign_vol_r_Tenor = foreign_vol_r.tenor;
            foreign_vol_r_Quote = foreign_vol_r.quote;

            sigmaTimes = unique(union([corr_drfr_Tenor(:);...
                         corr_drx_Tenor(:);corr_frx_Tenor(:);...
                         domestic_vol_r_Tenor(:);...
                         foreign_vol_r_Tenor(:)],fxBlackVolTenor));

            sigmaTimes = sort(sigmaTimes,'ascend');

            corr_drfr_Values = zeros(length(sigmaTimes),1);
            corr_drx_Values = zeros(length(sigmaTimes),1);
            corr_frx_Values = zeros(length(sigmaTimes),1);

            domestic_vol_r_Values = zeros(length(sigmaTimes), 1);
            foreign_vol_r_Values = zeros(length(sigmaTimes), 1);
            
            fxBlackVolValues = zeros(length(sigmaTimes),1);

            for k=1:length(sigmaTimes)
                corr_drfr_Values(k) = H_interpolation(corr_drfr_Tenor, corr_drfr_Quote,sigmaTimes(k),0);
                corr_drx_Values(k) = H_interpolation(corr_drx_Tenor, corr_drx_Quote,sigmaTimes(k),0);
                corr_frx_Values(k) = H_interpolation(corr_frx_Tenor, corr_frx_Quote,sigmaTimes(k),0);
                
                domestic_vol_r_Values(k) = H_interpolation(domestic_vol_r_Tenor, domestic_vol_r_Quote, sigmaTimes(k), 0);
                foreign_vol_r_Values(k) = H_interpolation(foreign_vol_r_Tenor, foreign_vol_r_Quote,sigmaTimes(k), 0);
                                
                fxBlackVolValues(k) = H_interpolation(fxBlackVolTenor, fxBlackVolQuote,sigmaTimes(k), 0);
            end
            
            % synchronize model parameters time-steps end
            % dummy correlation
            correl_1 = ones(length(sigmaTimes),1);
             
            var_x_x = eqDuire_ck1f.LocalVariance_Alpha2(a,b,sigmaTimes,fxBlackVolValues,fxBlackVolValues,correl_1);
            
            var_fr_fr = eqDuire_ck1f.GeneralVariance_HWHW(a,b,T,T,foreign_meanR_r,foreign_meanR_r,sigmaTimes, ...
                                        foreign_vol_r_Values,foreign_vol_r_Values,correl_1);
                                                     
            var_dr_dr = eqDuire_ck1f.GeneralVariance_HWHW(a,b,T,T,domestic_meanR_r, domestic_meanR_r, sigmaTimes,...
                                                         domestic_vol_r_Values, domestic_vol_r_Values, correl_1);
                                                     
           % 1st= sign in techNote , 2nd = HW bond vol? -1,1                               
            covar_fr_x =  1.0*-1.0*eqDuire_ck1f.GeneralVariance_BSHW(a,b,T,foreign_meanR_r,sigmaTimes, ...
                                            foreign_vol_r_Values,fxBlackVolValues,corr_frx_Values);
                                        
            covar_dr_x = -1.0*-1.0*eqDuire_ck1f.GeneralVariance_BSHW(a,b,T,domestic_meanR_r,sigmaTimes, ...
                                            domestic_vol_r_Values,domestic_Alpha_r_Values,fxBlackVolValues,corr_drx_Values);
                                        
            covar_dr_fr =  -1.0*1.0*eqDuire_ck1f.GeneralVariance_HWHW(a,b,T,T,domestic_meanR_r, foreign_meanR_r,sigmaTimes,...
                                            domestic_meanR_r,foreign_vol_r_Values, corr_drfr_Values);
                                                         
            value = var_x_x + var_fr_fr + var_dr_dr + 2.0 * (covar_fr_x + covar_dr_x + covar_dr_fr);                                         
            
            out = value;                                         
                                                     
            
        end
        
        function out = computeBSCK1FVariance(eqDuire_ck1f,a,b,T,corr_dre,...
                                  eqBlackVol, domestic_meanR_r, domestic_vol_r)
                                  
          % synchronize model parameters time-steps start 
            corr_dre_Tenor = corr_dre.tenor;
            corr_dre_Quote = corr_dre.quote;
            
            eqBlackVolTenor = eqBlackVol.tenor;
            eqBlackVolQuote = eqBlackVol.quote;

            domestic_vol_r_Tenor = domestic_vol_r.tenor;
            domestic_vol_r_Quote = domestic_vol_r.quote;
            
            sigmaTimes = unique(union([corr_dre_Tenor(:);...
                         domestic_vol_r_Tenor(:)],eqBlackVolTenor));

            sigmaTimes = sort(sigmaTimes,'ascend');

            corr_dre_Values = zeros(length(sigmaTimes),1);
            
            domestic_vol_r_Values = zeros(length(sigmaTimes), 1);
            
            eqBlackVolValues = zeros(length(sigmaTimes),1);

            for k=1:length(sigmaTimes)
                corr_dre_Values(k) = H_interpolation(corr_dre_Tenor, corr_dre_Quote,sigmaTimes(k),0);
                domestic_vol_r_Values(k) = H_interpolation(domestic_vol_r_Tenor, domestic_vol_r_Quote, sigmaTimes(k), 0);
                eqBlackVolValues(k) = H_interpolation(eqBlackVolTenor, eqBlackVolQuote,sigmaTimes(k), 0);
            
            end
            
            % synchronize model parameters time-steps end
            % dummy correlation
            correl_1 = ones(length(sigmaTimes),1);
             
            var_x_x = eqDuire_ck1f.LocalVariance_Alpha2(a,b,sigmaTimes,eqBlackVolValues,eqBlackVolValues,correl_1);
                                                     
%             var_dr_dr = eqDuire_ck1f.GeneralVariance_HWHW(a,b,T,T,domestic_meanR_r, domestic_meanR_r, sigmaTimes,...
%                                                          domestic_vol_r_Values, domestic_vol_r_Values, correl_1);
                                                     
           % 1st= sign in techNote , 2nd = HW bond vol? -1,1                               
            covar_dr_e = -1.0*-1.0*eqDuire_ck1f.GeneralVariance_BSHW(a,b,T,domestic_meanR_r,sigmaTimes, ...
                                            domestic_vol_r_Values,eqBlackVolValues,corr_dre_Values);
                                                         
%             value = var_x_x + var_dr_dr + 2.0 * (covar_dr_e);
            value = var_x_x + 2.0 * (covar_dr_e); 
            
            out = value;                                         
                                                     
            
        end
        
        function out = FindEQBlackVol(eqDuire_ck1f,index,params)
            
            expiry = params.eqImpVol.tenor(index);
            impVol = params.eqImpVol.quote(index);
            blackVariance = impVol * impVol * expiry;
            optParams.blackVariance = blackVariance;
            
            optParams.params = params;
            optParams.index = index;
            modelParamSize = 1;
            tvar = zeros(modelParamSize, 1);
            lb = zeros(modelParamSize, 1);
            ub = zeros(modelParamSize, 1);
            
            tvar(1) = params.eqImpVol.quote(index);
            lb(1)= 0.0001;
            ub(1)= 10;
            
            %options=[1E-03, 1E-25, 1E-25, 1E-25, 1E-25];
            options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-6];
            numOfEquation =1;
            x =  zeros(numOfEquation,1);
            [ret, popt, info, covar] = levmar('TargetFunctionBSCK1FVarianceSimple',tvar,x, 500, options,'unc',eqDuire_ck1f,optParams);
            
            out.eqBlackVol_index = popt(1);
            out.re = TargetFunctionBSCK1FVariance(popt,eqDuire_ck1f,optParams);
            out.marketVar = blackVariance;
            out.modelVar = (1.0+out.re)*blackVariance;
%             params.fxBlackVol.quote(index) = popt(1);

        end
        
        function out = CalibrateBSCK1FVol(eqDuire_ck1f, paramsIn)
            expirySize = length(paramsIn.eqImpVol.tenor);
            out.eqBlackVol.quote = zeros(expirySize,1);
            out.eqBlackVol.tenor = paramsIn.eqImpVol.tenor;
            out.re =  zeros(expirySize,1);
            out.modelVar = zeros(expirySize,1);
            out.marketVar = zeros(expirySize,1);
            out.rmseTotal = 0;

            for i = 1:expirySize
                index = i;
                BootstrapOut = eqDuire_ck1f.FindEQBlackVol(index,paramsIn);
                out.eqBlackVol.quote(i) = BootstrapOut.eqBlackVol_index;
                paramsIn.eqBlackVol.quote(i) = BootstrapOut.eqBlackVol_index;
                out.re(i) = BootstrapOut.re;
                out.marketVar(i) = BootstrapOut.marketVar;
                out.modelVar(i) = BootstrapOut.modelVar;
                out.rmseTotal = out.rmseTotal + out.re(i) * out.re(i);
            end
            
            out.rmseTotal = out.rmseTotal / expirySize;
            out.rmseTotal = sqrt(out.rmseTotal); 
                
        end
        
        
    end
    
end



In [ ]:
classdef EQBS_CK1F < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        % vol functor
        domestic_meanR_r;
        
        domestic_vol_r;
        
        %market input
        corr_de;
        
        %modelParams
        corr_dre;
        
        eqBlackVol;
        
        numOfFactors;
        modelType;
%         freq;
    end
    
    methods
        function eqDuire_ck1f = EQBS_CK1F(params)
            if nargin > 0
                eqDuire_ck1f.zeroCurve = params.eqModel.zeroCurve;
%                 eqDuire_ck1f.freq = params.eqModel.freq;
                eqDuire_ck1f.zeroCurve = params.eqModel.zeroCurve;
                eqDuire_ck1f.dividendCurve = params.eqModel.dividendCurve;
                eqDuire_ck1f.repoRateCurve = params.eqModel.repoRateCurve;
                eqDuire_ck1f.forwardCurve = params.eqModel.forwardCurve;
                
                eqDuire_ck1f.spot = params.eqModel.spot;
                eqDuire_ck1f.mktData =  params.eqModel.mktData;
                eqDuire_ck1f.modelParams = params.eqModel.modelParams;
                
                
                eqDuire_ck1f.numOfFactors = 1;
                eqDuire_ck1f.modelType = 'eqDuire_ck1f';
                
                eqDuire_ck1f.domestic_meanR_r = params.domesticModel.meanR_r;
                
                if params.eqVolCalibrated == true
                    % we do not calibrate eqBlackVol
                    eqDuire_ck1f.corr_de = params.corr_de;
                    
                    out = eqDuire_ck1f.synchronizeModelParams(params);
                                        
                    eqDuire_ck1f.corr_dre.tenor = out.sigmaTimes;
                    eqDuire_ck1f.corr_dre.quote = out.corr_dre_Values;
                    
                    eqDuire_ck1f.domestic_vol_r.tenor = out.sigmaTimes;
                    eqDuire_ck1f.domestic_vol_r.quote = out.domestic_vol_r_Values;
                                        
                    eqDuire_ck1f.eqBlackVol.tenor = out.sigmaTimes;
                    eqDuire_ck1f.eqBlackVol.quote = out.eqBlackVolValues;
                    
                else                    
                    % black vol calibration start
                    paramsIn.eqImpVol = params.eqBlackVol;
                    paramsIn.eqBlackVol = paramsIn.eqImpVol;
                    
                    paramsIn.domestic_meanR_r = params.domesticModel.meanR_r;
                    paramsIn.domestic_vol_r = params.domesticModel.vol_r;
                    
                    paramsIn.corr_de = params.corr_de;
                    
                    paramsIn.corr_dre = params.corr_dre;
                    
                     % BSCK1F Calibration Start
                    out = eqDuire_ck1f.CalibrateBSCK1FVol(paramsIn);
                    re =  out.re;
                    
                    marketVar = out.marketVar;
                    modelVar = out.modelVar;
                    rmseTotal = out.rmseTotal;
                    
                    % BSCK1F Calibration End
                    
                    params.eqBlackVol = out.eqBlackVol;
                    params.eqVolCalibrated =  true;
                    eqDuire_ck1f = EQBS_CK1F(params); 
                    
                end
            end
        end
        
        function out =  synchronizeModelParams(eqDuire_ck1f, params)
            eqBlackVolTenor = params.eqBlackVol.tenor;
            eqBlackVolQuote = params.eqBlackVol.quote;

            % synchronize model parameters time-steps start
            corr_dre_Tenor = params.corr_dre.tenor;
            corr_dre_Quote = params.corr_dre.quote;
            
            domestic_vol_r_Tenor = params.domesticModel.vol_r.tenor;
            domestic_vol_r_Quote = params.domesticModel.vol_r.quote;

            sigmaTimes = unique(union([corr_dre_Tenor(:);...
                         domestic_vol_r_Tenor(:)], eqBlackVolTenor));

            sigmaTimes = sort(sigmaTimes,'ascend');
            
            corr_dre_Values = zeros(length(sigmaTimes),1);
            
            domestic_vol_r_Values = zeros(length(sigmaTimes), 1);
            
            eqBlackVolValues = zeros(length(sigmaTimes),1);
            
            for k=1:length(sigmaTimes)
                corr_dre_Values(k) = H_interpolation(corr_dre_Tenor, corr_dre_Quote,sigmaTimes(k), 0);
                
                domestic_vol_r_Values(k) = H_interpolation(domestic_vol_r_Tenor, domestic_vol_r_Quote, sigmaTimes(k), 0);
                eqBlackVolValues(k) = H_interpolation(eqBlackVolTenor, eqBlackVolQuote,sigmaTimes(k),0);
            
            end
            
            out.sigmaTimes = sigmaTimes;
            
            out.corr_dre_Values = corr_dre_Values;
            
            out.domestic_vol_r_Values = domestic_vol_r_Values;
            out.eqBlackVolValues = eqBlackVolValues;
            
        end
        
        function out =  Libor_SimpleDate(eqDuire_ck1f, valueDate, evalTime, fwdStartTime, numMatTime, tenor, modelStatesT)
           % foreign Libor in domestic Terminal measure
           fwdStartDate = valueDate.AddDate(fwdStartTime,'day');
           fwdEndDate = fwdStartDate.AddDate(tenor,'year');
           fwdEndTime = fwdEndDate.DateDiff(valueDate);
           
           deltaT = (fwdEndTime - fwdStartTime)/365.0;
           numMatDate = valueDate.AddDate(numMatTime,'day');
           
           stateSize = size(modelStatesT,2);
           df_Tn = zeros(1,stateSize);
           df_TN = zeros(1,stateSize);
           
           df_Tn = eqDuire_ck1f.discountFactor(evalTime, fwdStartTime, numMatTime, modelStatesT);
           df_TN = eqDuire_ck1f.discountFactor(evalTime, fwdEndTime, numMatTime, modelStatesT);
           
           liborOut = zeros(1, stateSize);
           
           for i = 1:stateSize
                liborOut(i) = (df_Tn(i) / df_TN(i) - 1.0) / deltaT;
           end
           
           out = liborOut;
            
        end
        
        function out = CMS_SimpleDate(eqDuire_ck1f, valueDate, observeTime, numMatTime, tenor, modelStatesT)
           % CMT
%            tau = 0.25;
           tau = 1.0 / (eqDuire_ck1f.freq);
           % if tenor is 0.25(3M) then use tenor(0.25) instead
           % model(zeroCurve)'s freq
           
           if abs(tenor - 0.25) < 1e-8
                tau = tenor;
           end
           
           to     = observeTime / 365.0;
           toDate = valueDate.AddDate(observeTime, 'day');
           tNDate = toDate.AddDate(tenor, 'year');
           tNTime = tNDate.DateDiff(valueDate);
           tN     =  tNTime / 365.0;
           
           numMatDate = valueDate.AddDate(numMatTime, 'day');
           
           addMonthUnit = round(12 * tau);
           cnt = round((tN - to) / tau);
           
           stateSize = size(modelStatesT, 2);
           
           annuity = zeros(1, stateSize);
           df_Tp = zeros(1, stateSize);           
           df_Tn = zeros(1, stateSize);
           df_TN = zeros(1, stateSize);
           
           for i = 1:cnt
               tpDate = toDate.AddDate(i * addMonthUnit,'month');
               tpTime = tpDate.DateDiff(valueDate);
               df_Tp = eqDuire_ck1f.discountFactor(observeTime, tpTime, numMatTime, modelStatesT);
               annuity = annuity + tau * df_Tp;
           end
           
           df_Tn = eqDuire_ck1f.discountFactor(observeTime, observeTime, numMatTime, modelStatesT);
           df_TN = eqDuire_ck1f.discountFactor(observeTime, tNTime, numMatTime, modelStatesT);
           
           cms_PCA_SimpleOut = zeros(1, stateSize);
           
           for i = 1:stateSize
                cms_PCA_SimpleOut(i) = (df_Tn(i) - df_TN(i)) / annuity(i);
           end
           
           out = cms_PCA_SimpleOut;
            
        end
        
         % Should check variance functions for HWHW later. 2020-02-18 by LIB
         function out =  CMS_PSA_SimpleDate(eqDuire_ck1f,valueDate,observeTime,numMatTime, tenor,modelStatesT)
           %CMT
%            tau = 0.25;
           tau = 1.0/(eqDuire_ck1f.freq);
            % if tenor is 0.25(3M) then use tenor(0.25) instead
           % model(zeroCurve)'s freq
           
           if abs(tenor- 0.25) < 1e-8
                tau = tenor;
           end
           
           to      = observeTime/365.0;
           toDate = valueDate.AddDate(observeTime,'day');
           tNDate = toDate.AddDate(tenor,'year');
           tN   =  tNDate.DateDiff(valueDate)/365.0;
           
           numMatDate = valueDate.AddDate(numMatTime,'day');
           
           p_nN = eqDuire_ck1f.PV01Date(valueDate,toDate,tNDate,tau);
           
           df_Tn = eqDuire_ck1f.DF(to);
           df_TN = eqDuire_ck1f.DF(tN);
           y_nN = (df_Tn - df_TN)/p_nN;
           
           c_nN = eqDuire_ck1f.C_nNDate(valueDate,toDate,tNDate,tau,p_nN,y_nN);
           g_nN = eqDuire_ck1f.G_nNDate(valueDate,toDate,tNDate,tau,p_nN);
%            h_nTerm = eqDuire_ck1f.H_nTermDate(valueDate,toDate,numMatDate);
           
           %h_nTerm is replace by i_Term & i_Tn_tilda in the following
           
           h_nTerm(1) = 0.0;
           
           varCovar = eqDuire_ck1f.LocalVariance(0,to);
           
           stateSize = size(modelStatesT,2);
           cms_PCA_SimpleOut = zeros(1,stateSize);
           
           driftTerm = 0;
           for i=1:1
               for j=1:1
                   driftTerm = driftTerm + (c_nN(i) * h_nTerm(j) + c_nN(i) * g_nN(j))*varCovar(i,j);
               end
           end
           
           % additional drift correction term from foreign Term USD to
           % domestic Term measure KRW
           i_Term = I_Term(eqDuire_ck1f,0,to,numMatTime/365.0);
           i_Tn_tilda = I_Tn_tilda(eqDuire_ck1f,0,to,to);
           j_x_tilda = J_x_tilda(eqDuire_ck1f,0,to,to);
           
%            additionalDrift = 0;
           additionalDrift = c_nN(1) * (i_Term + i_Tn_tilda + j_x_tilda);
           
           for i=1:stateSize
               cms_PCA_SimpleOut(i) = y_nN + driftTerm + additionalDrift + c_nN(1)*modelStatesT(1,i); 
           end
           
           out = cms_PCA_SimpleOut;
           
            
         end
         
%          function out = Foreign_HtT_r(eqDuire_ck1f,t,T)
%             out =  eqDuire_ck1f.H(T,eqDuire_ck1f.foreign_dH) - eqDuire_ck1f.H(t,eqDuire_ck1f.foreign_dH); 
%          end
%          
%          function out = Domestic_HtT_r(eqDuire_ck1f,t,T)
%             out =  eqDuire_ck1f.H(T,eqDuire_ck1f.domestic_dH) - eqDuire_ck1f.H(t,eqDuire_ck1f.domestic_dH); 
%          end
         
%          function out = H(eqDuire_ck1f,t,dH)
%             for i=1:length(dH.tenor)
%                 if t<= dH.tenor(i)
%                     break;
%                 end
%             end
%             tidx = i;
%             sum = 0.0;
%             prev_t = 0.0;
%             curr_t = 0.0;
%             for i=1:tidx
%                 if i< tidx
%                     curr_t = dH.tenor(i);
%                 else
%                     curr_t = t;
%                 end
%                 sum = sum + dH.quote(i)*(curr_t-prev_t);
% 
%                 prev_t = dH.tenor(i);
%             end
%             out = sum;
%          end

        function out = EQSpotMC(eqDupire_ck1f,valueDate,observeTime,numMatTime,irModelStatesT,eqModelStatesT)
        
            spotPrice = eqDupire_ck1f.spot.params('rawData');
            detFwd = eqDupire_ck1f.Fwd(spotPrice,observeTime); 
             
            meanR = eqDupire_ck1f.domestic_meanR_r;
            
             %stochasticFwd(0,T)
             
             stateSize = length(eqModelStatesT);
             stochasticFwd = zeros(stateSize,1);
             
             fwdVarianceEQOut = eqDupire_ck1f.FwdVarianceEQ(0,observeTime/365.0,numMatTime/365.0);
             for i=1:stateSize
                stochasticFwd(i) = detFwd * exp(eqModelStatesT(i) -1.0/meanR * irModelStatesT(i) -0.5*fwdVarianceEQOut);
%                 stochasticFwd(i) = detFwd * exp(eqModelStatesT(i) -0.5*fwdVarianceEQOut); 
             end
             
             out = stochasticFwd;
        
        end
        
        function out = FwdVarianceEQ(eqDuire_ck1f, from, to, Tnum)
            
            localVariance = zeros(3,1);
            measureChange = zeros(3,1);
            quantoChange = zeros(2,1);
            
            sigmaTimes = eqDuire_ck1f.domestic_vol_r.tenor;
            
            domestic_vol_r_Values = eqDuire_ck1f.domestic_vol_r.quote;
            meanR = eqDuire_ck1f.domestic_meanR_r;
            eqBlackVolValues =  eqDuire_ck1f.eqBlackVol.quote;
            
            correl_1 = ones(length(sigmaTimes),1);
            corr_dre_Values = eqDuire_ck1f.corr_dre.quote;
            
            localVariance(1) = eqDuire_ck1f.LocalVariance_Alpha2(from,to,sigmaTimes,eqBlackVolValues,eqBlackVolValues,correl_1);
            localVariance(2) = eqDuire_ck1f.GeneralVariance_BSHW(from,to,to,meanR,sigmaTimes,domestic_vol_r_Values,eqBlackVolValues,corr_dre_Values);
            localVariance(3) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,to,to,meanR,meanR,sigmaTimes,domestic_vol_r_Values,domestic_vol_r_Values,correl_1);
            
%             quantoChange(1) = -1.0*eqDuire_ck1f.GeneralVariance_BSHW(from,to,T1,MRS_fr,sigmaTimes,foreign_vol_r_Values,fxValues,corr_frx_Values);
%             quantoChange(2) = -1.0*eqDuire_ck1f.GeneralVariance_BSHW(from,to,to,MRS_fr,sigmaTimes,foreign_vol_r_Values,fxValues,corr_frx_Values);
            
            measureChange(1) = eqDuire_ck1f.LocalVariance_HW_Alpha(from,to,to,meanR,sigmaTimes,domestic_vol_r_Values,eqBlackVolValues,corr_dre_Values);
            measureChange(2) = eqDuire_ck1f.LocalVariance_HW_Alpha(from,to,to,meanR,sigmaTimes,domestic_vol_r_Values,domestic_vol_r_Values,correl_1);
            
            measureChange(3) = eqDuire_ck1f.LocalVariance_HWHW(from,to,to,to,meanR,meanR,sigmaTimes,domestic_vol_r_Values,domestic_vol_r_Values,correl_1);
            
            value = localVariance(1) + 2.0 * localVariance(2) + localVariance(3);
            
            betaTerm = eqDuire_ck1f.Beta(to,Tnum);
            
            value = value - 2.0 * -1.0 * betaTerm*(measureChange(1) + 1.0/meanR*(measureChange(2) - measureChange(3)));    
            
            out = value;
        
        end
        
        function out = fwdZcVarianceForeign(eqDuire_ck1f, from, to, T1, T2)
            localVariance = zeros(2,1);
            measureChange = zeros(2,1);
            quantoChange = zeros(2,1);
            
            sigmaTimes = eqDuire_ck1f.domestic_vol_r.tenor;
            
            domestic_vol_r_Values = eqDuire_ck1f.domestic_vol_r.quote;
            foreign_vol_r_Values = eqDuire_ck1f.foreign_vol_r.quote;
            
            fxValues = eqDuire_ck1f.fxBlackVol.quote;
            
            MRS_dr = eqDuire_ck1f.domestic_meanR_r;
            MRS_fr = eqDuire_ck1f.foreign_meanR_r;
            
            correl_1 = ones(length(sigmaTimes),1);
            corr_frx_Values = eqDuire_ck1f.corr_frx.quote;
            corr_drfr_Values = eqDuire_ck1f.corr_drfr.quote;
            
            localVariance(1) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,T1,T1,MRS_fr,MRS_fr,sigmaTimes,foreign_vol_r_Values,foreign_vol_r_Values,correl_1);
            localVariance(2) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,to,to,MRS_fr,MRS_fr,sigmaTimes,foreign_vol_r_Values,foreign_vol_r_Values,correl_1);
            
            quantoChange(1) = -1.0*eqDuire_ck1f.GeneralVariance_BSHW(from,to,T1,MRS_fr,sigmaTimes,foreign_vol_r_Values,fxValues,corr_frx_Values);
            quantoChange(2) = -1.0*eqDuire_ck1f.GeneralVariance_BSHW(from,to,to,MRS_fr,sigmaTimes,foreign_vol_r_Values,fxValues,corr_frx_Values);
            
            measureChange(1) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,T1,T2,MRS_fr,MRS_dr,sigmaTimes,foreign_vol_r_Values,domestic_vol_r_Values,corr_drfr_Values);
            measureChange(2) = eqDuire_ck1f.GeneralVariance_HWHW(from,to,to,T2,MRS_fr,MRS_dr,sigmaTimes,foreign_vol_r_Values,domestic_vol_r_Values,corr_drfr_Values);
            
            value = localVariance(1) - localVariance(2);
            value = value - 2.0 * -1.0 * (quantoChange(1) - quantoChange(2));
            value = value - 2.0 * 1.0 * (measureChange(1) - measureChange(2));    
            
            out = value;
            
        end
        
        function beta = Beta(eqDuire_ck1f, t, T)
            a_r = eqDuire_ck1f.domestic_meanR_r;
            beta =[];
            
            if(abs(a_r) > 1.0E-12)
                beta(1) = (1.0 - exp(-a_r * (T - t))) / a_r;
            else
                beta(1) = (T - t);
            end
            
        end
        
        function beta = BetaDate(eqDuire_ck1f, valueDate, tDate, TDate)
            t = tDate.DateDiff(valueDate) / 365.0;
            T = TDate.DateDiff(valueDate) / 365.0;
            
            a_r = eqDuire_ck1f.foreign_meanR_r;
            beta =[];
            
            if(abs(a_r) > 1.0E-12)
                beta(1) = (1.0 - exp(-a_r * (T - t))) / a_r;
            else
                beta(1) = (T-t);
            end
            
        end
        
        function c_nN = C_nN(eqDuire_ck1f, tn, tN, tau, pnN, ynN)
            p = @eqDuire_ck1f.DF;
            c_nN = [0.0];
            
            for i = 1:round((tN - tn) / tau)
                tp = tn + i * tau;
                beta = eqDuire_ck1f.Beta(tn, tp);
                df = p(tp);
                c_nN(1) = c_nN(1) +tau * beta(1) * df;
            end
            
            c_nN(1) = c_nN(1) * ynN;
            c_nN(1) = c_nN(1) + beta(1) * df;
            c_nN(1) = c_nN(1) / pnN;
            
        end
        
        function c_nN = C_nNDate(eqDuire_ck1f,valueDate,tnDate,tNDate,tau,pnN,ynN)
            tn = tnDate.DateDiff(valueDate) / 365.0;
            tN = tNDate.DateDiff(valueDate) / 365.0;
            
            addMonthUnit = round(12*tau);
            cnt = round((tN-tn)/tau);
            
            p = @eqDuire_ck1f.DF;
            c_nN=[0.0];
            beta = [0.0];
            df = 0.0;
            prevTime = tn;
            deltaT = 0.0;
            for i=1:cnt
                tpDate = tnDate.AddDate(i*addMonthUnit,'month');
                tp = tpDate.DateDiff(valueDate)/365.0;
                deltaT = tp - prevTime;
                beta = eqDuire_ck1f.BetaDate(valueDate,tnDate,tpDate);
                df = p(tp);
%                 c_nN(1) = c_nN(1) +tau * beta(1) * df;
                c_nN(1) = c_nN(1) +deltaT * beta(1) * df;
                prevTime = tp;
            end
            
            c_nN(1) = c_nN(1)* ynN;
            
            c_nN(1) = c_nN(1) + beta(1)*df;
            
            c_nN(1) = c_nN(1)/pnN;
        end
        
        function g_nN = G_nN(eqDuire_ck1f,tn,tN,tau,pnN)
            p = @eqDuire_ck1f.DF;
            g_nN=[0.0];
            
            for i=1:round((tN-tn)/tau)
                tp = tn+i*tau;
                beta = eqDuire_ck1f.Beta(tn,tp);
                df = p(tp);
                g_nN(1) = g_nN(1) +tau * beta(1) * df;
            end
            
            g_nN(1) = g_nN(1)/pnN;
        end
        
        function g_nN = G_nNDate(eqDuire_ck1f,valueDate,tnDate,tNDate,tau,pnN)
            tn = tnDate.DateDiff(valueDate)/365.0;
            tN = tNDate.DateDiff(valueDate)/365.0;
            addMonthUnit = round(12*tau);
            cnt = round((tN-tn)/tau);
            
            p = @eqDuire_ck1f.DF;
            g_nN=[0.0];
            
            prevTime = tn;
            deltaT = 0.0;
            for i=1:cnt
                tpDate = tnDate.AddDate(i*addMonthUnit,'month');
                tp = tpDate.DateDiff(valueDate)/365.0;
                deltaT = tp - prevTime;
                beta = eqDuire_ck1f.BetaDate(valueDate,tnDate,tpDate);
                df = p(tp);
%                 g_nN(1) = g_nN(1) +tau * beta(1) * df;
                g_nN(1) = g_nN(1) + deltaT * beta(1) * df;
                prevTime = tp;
            end
            
            g_nN(1) = g_nN(1)/pnN;
        end
        
        function h_nTerm = H_nTerm(eqDuire_ck1f,tn,tTerm)
           h_nTerm =[];
           beta = eqDuire_ck1f.Beta(tn,tTerm);
           h_nTerm(1) = -1.0*beta(1);
        end
        
        function h_nTerm = H_nTermDate(eqDuire_ck1f,valueDate,tnDate,tTermDate)
           h_nTerm =[];
           beta = eqDuire_ck1f.BetaDate(valueDate,tnDate,tTermDate);
           h_nTerm(1) = -1.0*beta(1);
        end
        
        function i_Term = I_Term(eqDuire_ck1f,from,to,tTerm)

            fMRS = eqDuire_ck1f.foreign_meanR_r;
            sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
            foreign_vol_r_Values = eqDuire_ck1f.foreign_vol_r.quote;
            
            dMRS = eqDuire_ck1f.domestic_meanR_r;
            domestic_vol_r_Values = eqDuire_ck1f.domestic_vol_r.quote;
            
            corr_drfr_Values = eqDuire_ck1f.corr_drfr.quote;
                        
            % QuantoCK1F_LGM2F case
%             variance_drfr = eqDuire_ck1f.GeneralVariance_HWLGM_type2(from,to,to,tTerm,MRS1,sigmaTimes,domestic_dH_r_Values,domestic_Alpha_r_Values,...
%                                                          foreign_vol_r_Values,corr_drfr_Values);
            
            % eqDuire_ck1f case
            variance_drfr = eqDuire_ck1f.GeneralVariance_HWHW_type2(from, to, to, tTerm, dMRS, fMRS, sigmaTimes,...
                                                            domestic_vol_r_Values, foreign_vol_r_Values, corr_drfr_Values);
            
            % we add minus 1 so that we don't need additional minus in
            % drift adjust term
            i_Term = -1.0 * (variance_drfr);
           
        end
        
        function i_Tn_tilda = I_Tn_tilda(eqDuire_ck1f,from,to,tn)

            MRS1 = eqDuire_ck1f.foreign_meanR_r;
            sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
            foreign_vol_r_Values = eqDuire_ck1f.foreign_vol_r.quote;
            corr_frfr_Values = ones(length(sigmaTimes),1);
            
            variance_frfr = eqDuire_ck1f.GeneralVariance_HWHW_type2(from,to,tn,tn,MRS1,MRS1,sigmaTimes,...
                                                                        foreign_vol_r_Values,foreign_vol_r_Values,corr_frfr_Values);
           % we don't need minus 1
           i_Tn_tilda = 1.0 * variance_frfr;
           
        end
        
%         function i_Tn_tilda = I_Tn_tilda_old(eqDuire_ck1f,from,to,tn)
% 
%             sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
%             sigmaSize =  length(sigmaTimes);
%             
%             for i=1:sigmaSize
%                 if from<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             startIdx = i;
%             
%             for i=1:sigmaSize
%                 if to<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             endIdx = i;
%            
%            MRS2 = eqDuire_ck1f.foreign_meanR_r;
%            
%            newExpScale = zeros(2,1);
%            lastExpScale = zeros(2,1);
%            variances = zeros(2,1);
%             
%            lastU  = from;
%            
%            lastExpScale(1) = exp(MRS2*lastU);
%            lastExpScale(2) = exp((MRS2 + MRS2)*lastU);
%            
%            sigmaValues1 = eqDuire_ck1f.foreign_vol_r.quote;
%            sigmaValues2 = eqDuire_ck1f.foreign_vol_r.quote;
%            corr12 = 1.0;
% 
%            
%            for i=startIdx:endIdx
%                 if (i< endIdx) U = sigmaTimes(i);else U = to;end;
%                 if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
%                 if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
%                 
%                 newExpScale(1) = exp(MRS2*U);
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(1)-lastExpScale(1));
%                 lastExpScale(1) = newExpScale(1);
%                 
%                 newExpScale(2) = exp((MRS2+MRS2)*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/(MRS2+MRS2)) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
%                 
%                 lastU = U;
%            end
%            
%            value = exp(-1.0*MRS2*tn)*(1.0/ MRS2)*variances(1);
%            value = value + -1.0*exp(-1.0*(MRS2 + MRS2)*tn)*(1.0/ MRS2)*variances(2);
%            % we don't need minus 1
%            i_Tn_tilda = 1.0 * value;
%            
%         end
        
        
        
        function j_x_tilda = J_x_tilda(eqDuire_ck1f,from,to,tn)

            MRS1 = eqDuire_ck1f.foreign_meanR_r;
            sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
            foreign_vol_r_Values = eqDuire_ck1f.foreign_vol_r.quote;
            fxBlackVol_Values = eqDuire_ck1f.fxBlackVol.quote;
            corr_frx_Values = eqDuire_ck1f.corr_frx.quote;
            
            variance_frx = eqDuire_ck1f.GeneralVariance_BSHW_type2(from,to,tn,MRS1,sigmaTimes,...
                                                                        foreign_vol_r_Values,fxBlackVol_Values,corr_frx_Values);
           
           % we need minus 1
           j_x_tilda = -1.0 * variance_frx;
           
        end
        
%         function j_x_tilda = J_x_tilda_old(eqDuire_ck1f,from,to,tn)
% 
%             sigmaTimes = eqDuire_ck1f.foreign_vol_r.tenor;
%             sigmaSize =  length(sigmaTimes);
%             
%             for i=1:sigmaSize
%                 if from<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             startIdx = i;
%             
%             for i=1:sigmaSize
%                 if to<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             endIdx = i;
%            
%             
%            newExpScale = zeros(1,1);
%            lastExpScale = zeros(1,1);
%            
%            lastU  = from;
%            MRS2 = eqDuire_ck1f.foreign_meanR_r;
%            lastExpScale(1) = exp(MRS2*lastU);
%            variances = 0.0;
%            
%            sigmaValues1 = eqDuire_ck1f.fxBlackVol.quote;
%            sigmaValues2 = eqDuire_ck1f.foreign_vol_r.quote;
%            corrValues12 = eqDuire_ck1f.corr_frx.quote;
%            
%            for i=startIdx:endIdx
%                 if (i< endIdx) U = sigmaTimes(i);else U = to;end;
%                 if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
%                 if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
%                 if (i< sigmaSize) corr12 = corrValues12(i);else corr12 = corrValues12(sigmaSize);end;
%                 
%                 newExpScale(1) = exp(MRS2*U);
%                 variances = variances + corr12 * vol1 * vol2 * (1.0/MRS2) * (newExpScale(1)-lastExpScale(1));
%                 lastExpScale(1) = newExpScale(1);
%                 
%                 lastU = U;
%            end
%            
%            % we need minus 1
%            j_x_tilda = -1.0 * exp(-1.0*MRS2*tn) * (1.0/MRS2) * variances;
%            
%         end
        
        function out = discountFactor(eqDuire_ck1f, startTime, endTime, numMatTime, modelStatesT) 
           zcT = eqDuire_ck1f.DF(endTime/365.0);
           
           %numOfPath
           stateSize = size(modelStatesT, 2);
           discountFactorOut = zeros(1, stateSize);
           
           % deterministic discount factor
           if startTime <= 1e-8
               for i = 1:stateSize
                   discountFactorOut(i) = zcT;
               end
                
               out = discountFactorOut;
               return;
           end
           
           % deterministic discount factor or maturity in the past
           if startTime >= endTime
               out = ones(1,stateSize);
               return;
           end
           
           zct = eqDuire_ck1f.DF(startTime / 365.0);
           beta = eqDuire_ck1f.Beta(startTime/365.0, endTime/365.0);
           zcDriftTerm = eqDuire_ck1f.fwdZcVarianceForeign(0, startTime/365.0, endTime/365.0, numMatTime/365.0);
           
           % eqDuire_ck1f is one factor model
           for i = 1:stateSize
%                discountFactorOut(i) = zcT/zct * exp(-0.5*zcDriftTerm - beta(1)*modelStatesT(1,i));
               discountFactorOut(i) = zcT / zct * exp(-0.5 * zcDriftTerm - beta(1) * modelStatesT(1, i));
           end
           
           out = discountFactorOut;
           
        end
        
%         function out = discountPayoff(eqDuire_ck1f,eventTime,numMatTime ...
%                 ,modelStatesT,cashflow)
%             
%             dfNumMat = eqDuire_ck1f.GetChildModel('d').DF(numMatTime/365.0);
%             % for discountPayoff T=numMatTime
%             % P(0,TnumMat)/P(Te,Tnummat)*Payoff
%             %
%             domesticModelStatesT = modelStatesT(1,:);
%             discountT = eqDuire_ck1f.GetChildModel('d').discountFactor(eventTime, numMatTime,numMatTime,domesticModelStatesT);
%             stateSize = size(modelStatesT,2);
%             payoff = zeros(1,stateSize);
%             for i=1:stateSize
%                 payoff(i)= dfNumMat/discountT(i)*cashflow(i);
%             end    
%             out = payoff;
%         end
        
        function variances = LocalVariance(eqDuire_ck1f,from,to)

            sig(1) = eqDuire_ck1f.foreign_vol_r;
            meanR(1) = eqDuire_ck1f.foreign_meanR_r;
            
            alphaSize = length(sig(1).quote);
            
            for i=1:length(sig(1).tenor)
                if from<= sig(1).tenor(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sig(1).tenor)
                if to<= sig(1).tenor(i)
                    break;
                end
            end
            endIdx = i;
            
            tiny = zeros(1,1);
            lastExpScale = zeros(1,1);
            newExpScale  = zeros(1,1);
            
            for i=1:1
                for j=1:1
                    if(abs(meanR(i)+meanR(j)) < 1.0E-12) tiny(i,j) = 1; else tiny(i,j) = 0; end
                    lastExpScale(i,j) =  exp((meanR(i)+meanR(j))*from);
                end
            end
  
           lastU  = from;
           
           variances = zeros(1,1);
           
           for i=startIdx:endIdx
                if (i< endIdx) U = sig(1).tenor(i);else U = to;end;
                if (i< alphaSize) vol(1) = sig(1).quote(i);else vol(1) = sig(1).quote(alphaSize);end;
                
                correl =ones(1,1);
                for j=1:1
                    for k=1:1
                        newExpScale(j,k) =  exp((meanR(j)+meanR(k))*U);
                        if(tiny(j,k)~=1)
                            scale =newExpScale(j,k)-lastExpScale(j,k);
                        else
                            scale = U - lastU;
                        end
                        variances(j,k) = variances(j,k) + vol(j)*vol(k)*correl(j,k)...
                                       * scale;
                        lastExpScale(j,k) = newExpScale(j,k);
                    end
                end
                lastU = U;
           end
           
           for j=1:1
                for k=1:1
                    if(tiny(j,k)~= 1)
                        variances(j,k) = variances(j,k)/(meanR(j)+meanR(k))*exp(-1.0*(meanR(j)+meanR(k))*to);
                    end
                end
           end
           
        end
        
        function out = LocalDrift(eqDuire_ck1f,from,to)
            drift = eye(2,2);
            drift(1,1) = exp(-1.0*eqDuire_ck1f.domestic_meanR_r*(to-from));
            drift(2,2) = 1.0;
            out = drift;
        end
        
        function variances = LocalCovariance(eqDuire_ck1f,from,to)

            % Covariance Between,
            % X(t) ~ int{from,to}_{exp(-a*(to-u))*sigma_d(u)*dW_d(u)} &
            % Z(t) ~ int{from,to}_{sigma_e(u)*dW_e(u)-1/a*sigma_d(u)*dW_d(u)}

            sigmaValue1 = eqDuire_ck1f.domestic_vol_r.quote;
            sigmaValue2 = eqDuire_ck1f.eqBlackVol.quote;
            
            corr12 = eqDuire_ck1f.corr_dre.quote;
            meanR = eqDuire_ck1f.domestic_meanR_r;
            sigmaTimes = eqDuire_ck1f.domestic_vol_r.tenor;
            corr11 = 1.0*ones(length(sigmaTimes),1);
            
            variances = zeros(2, 2);
            
            variances(1,1) = eqDuire_ck1f.LocalVariance_HWHW(from,to,to,to,meanR,meanR,sigmaTimes,sigmaValue1,sigmaValue1,corr11);
            
            
            variances12 = eqDuire_ck1f.LocalVariance_HW_Alpha(from,to,to,meanR,sigmaTimes,sigmaValue1,sigmaValue2,corr12);
            variances12 = variances12 +1.0/meanR*eqDuire_ck1f.LocalVariance_HW_Alpha(from,to,to,meanR,sigmaTimes,sigmaValue1,sigmaValue1,corr11);
            variances(1,2) = variances12;
            
            variances(2,1) = variances(1,2);
            
            variance22 = eqDuire_ck1f.LocalVariance_Alpha2(from,to,sigmaTimes,sigmaValue2,sigmaValue2,corr11);
            variance22 = variance22 +     2.0*1.0/meanR*eqDuire_ck1f.LocalVariance_Alpha2(from,to,sigmaTimes,sigmaValue1,sigmaValue2,corr12);
            variance22 = variance22 +1.0/meanR*1.0/meanR*eqDuire_ck1f.LocalVariance_Alpha2(from,to,sigmaTimes,sigmaValue1,sigmaValue1,corr11);
            
            variances(2,2) = variance22;
           
            
        end
        
        function out = LocalVariance_HW_Alpha(eqDuire_ck1f,from,to,T1,MRS1,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [from,to] of e^{-a(T1-s)}*sigma1(s)sigma2(s)
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(4,1);
            lastExpScale = zeros(4,1);
            variances = zeros(4,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS1*lastU);
%             lastExpScale(3) = exp(MRS2*lastU);
%             lastExpScale(4) = exp((MRS1 + MRS2)*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end;
                
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
                newExpScale(2) = exp(MRS1*U);
                variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
                lastExpScale(2) = newExpScale(2);
                
%                 newExpScale(3) = exp(MRS2*U);
%                 variances(3) = variances(3) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(3)-lastExpScale(3));
%                 lastExpScale(3) = newExpScale(3);
%                 
%                 newExpScale(4) = exp((MRS1+MRS2)*U);
%                 variances(4) = variances(4) + corr12 * sig1 * sig2 * (1.0/(MRS1+MRS2)) * (newExpScale(4)-lastExpScale(4));
%                 lastExpScale(4) = newExpScale(4);
                
                lastU = U;
                
            end
            
%             value = (1.0/ MRS1)*(1.0/MRS2)*variances(1);
%             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*(1.0/MRS2)*variances(2);
%             value = value + -1.0*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(3);
%             value = value +  1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(4);

%             value = 1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*variances(2);
            
            value = 1.0*exp(-1.0*MRS1*T1)*variances(2);
            out  = value;
        end
        
        function out = LocalVariance_HWHW(eqDuire_ck1f,from,to,T1,T2,MRS1,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)

            % Variance in [from,to] of
            % e^{-a(T1-s)}*e^{-b(T2-s)}*sigma1(s)*sigma2(s)*corr12(s)
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(4,1);
            lastExpScale = zeros(4,1);
            variances = zeros(4,1);
            
            lastU  = from;
%             lastExpScale(2) = exp(MRS1*lastU);
%             lastExpScale(3) = exp(MRS2*lastU);
            lastExpScale(4) = exp((MRS1 + MRS2)*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end;
                
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
%                 
%                 newExpScale(2) = exp(MRS1*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
%                 
%                 newExpScale(3) = exp(MRS2*U);
%                 variances(3) = variances(3) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(3)-lastExpScale(3));
%                 lastExpScale(3) = newExpScale(3);
%                 
                newExpScale(4) = exp((MRS1+MRS2)*U);
                variances(4) = variances(4) + corr12 * sig1 * sig2 * (1.0/(MRS1+MRS2)) * (newExpScale(4)-lastExpScale(4));
                lastExpScale(4) = newExpScale(4);
                
                lastU = U;
                
            end
            
%             value = (1.0/ MRS1)*(1.0/MRS2)*variances(1);
%             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*(1.0/MRS2)*variances(2);
%             value = value + -1.0*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(3);
%             value = 1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(4);
            value = 1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*variances(4);

            out  = value;
        end
        
        function out = LocalVariance_H2_Alpha2(eqDuire_ck1f,from,to,sigmaTimes,dH1Values, dH2Values, sigmaValues1,sigmaValues2,corrValues)

            sigmaSize =  length(sigmaTimes);
            
            for i=1:sigmaSize
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:sigmaSize
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
  
           lastU  = from;
           
           variances = 0.0;
           
           dH1.quote = dH1Values;
           dH1.tenor = sigmaTimes;
           
           dH2.quote = dH2Values;
           dH2.tenor = sigmaTimes;
           
           for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
                if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
                if (i< sigmaSize) dH1Value = dH1.quote(i);else dH1Value = dH1.quote(sigmaSize);end;
                if (i< sigmaSize) dH2Value = dH2.quote(i);else dH2Value = dH2.quote(sigmaSize);end;
                if (i< sigmaSize) correl = corrValues(i);else correl = corrValues(sigmaSize);end;
                
                variances = variances + eqDuire_ck1f.H(lastU,dH1)*eqDuire_ck1f.H(lastU,dH2)*correl*vol1*vol2*(U - lastU);
                variances = variances + dH1Value*eqDuire_ck1f.H(lastU,dH2)*correl*vol1*vol2*0.5*(U - lastU)*(U - lastU);
                variances = variances + eqDuire_ck1f.H(lastU,dH1)*dH2Value*correl*vol1*vol2*0.5*(U - lastU)*(U - lastU);
                variances = variances + dH1Value*dH2Value*correl*vol1*vol2*1.0/3.0*(U - lastU)*(U - lastU)*(U - lastU);
                
                
                lastU = U;
           end
           
           out = variances;
           
        end
        
        function out = LocalVariance_H_Alpha2(eqDuire_ck1f,from,to,sigmaTimes,dH1Values,sigmaValues1,sigmaValues2,corrValues)

            sigmaSize =  length(sigmaTimes);
            
            for i=1:sigmaSize
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:sigmaSize
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
  
           lastU  = from;
           
           variances = 0.0;
           
           dH1.quote = dH1Values;
           dH1.tenor = sigmaTimes;
           
           for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
                if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
                if (i< sigmaSize) dH = dH1.quote(i);else dH = dH1.quote(sigmaSize);end;
                if (i< sigmaSize) correl = corrValues(i);else correl = corrValues(sigmaSize);end;
                
                variances = variances + eqDuire_ck1f.H(lastU,dH1) * correl * vol1 * vol2 * (U - lastU);
                variances = variances + 0.5 * dH * correl * vol1 * vol2 * (U - lastU) * (U - lastU);
                lastU = U;
           end
           
           out = variances;
           
        end
        
        function out = LocalVariance_Alpha2(eqDuire_ck1f,from,to,sigmaTimes,sigmaValues1,sigmaValues2,corrValues)

            sigmaSize =  length(sigmaTimes);
            
            for i=1:sigmaSize
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:sigmaSize
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
  
           lastU  = from;
           
           variances = 0.0;
           
           for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) vol1 = sigmaValues1(i);else vol1 = sigmaValues1(sigmaSize);end;
                if (i< sigmaSize) vol2 = sigmaValues2(i);else vol2 = sigmaValues2(sigmaSize);end;
                if (i< sigmaSize) correl = corrValues(i);else correl = corrValues(sigmaSize);end;
                
                variances = variances + correl* vol1 * vol2 * (U - lastU);
                lastU = U;
           end
           
           out = variances;
           
        end
        
        function out = GeneralVariance_HWHW(eqDuire_ck1f,from,to,T1,T2,MRS1,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [from,to] of 1/a*(1-e^{-a(T1-s)})*1/b*(1-e^{-b(T2-s)})sigma1(s)sigma2(s)
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(4,1);
            lastExpScale = zeros(4,1);
            variances = zeros(4,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS1*lastU);
            lastExpScale(3) = exp(MRS2*lastU);
            lastExpScale(4) = exp((MRS1 + MRS2)*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end;
                
                variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
                newExpScale(2) = exp(MRS1*U);
                variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
                lastExpScale(2) = newExpScale(2);
                
                newExpScale(3) = exp(MRS2*U);
                variances(3) = variances(3) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(3)-lastExpScale(3));
                lastExpScale(3) = newExpScale(3);
                
                newExpScale(4) = exp((MRS1+MRS2)*U);
                variances(4) = variances(4) + corr12 * sig1 * sig2 * (1.0/(MRS1+MRS2)) * (newExpScale(4)-lastExpScale(4));
                lastExpScale(4) = newExpScale(4);
                
                lastU = U;
                
            end
            
            value = (1.0/ MRS1)*(1.0/MRS2)*variances(1);
            value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*(1.0/MRS2)*variances(2);
            value = value + -1.0*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(3);
            value = value +  1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*(1.0/MRS2)*variances(4);

            out  = value;
        end
        
        function out = GeneralVariance_HWHW_type2(eqDuire_ck1f,from,to,T1,T2,MRS1,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [a,b] of 1/a*(1-e^{-a(T1-s)})*e^{-b(T2-s)}*sigma1(s)sigma2(s)
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(4,1);
            lastExpScale = zeros(4,1);
            variances = zeros(4,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS1*lastU);
            lastExpScale(3) = exp(MRS2*lastU);
            lastExpScale(4) = exp((MRS1 + MRS2)*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end;
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end;
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end;
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end;
                
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
%                 newExpScale(2) = exp(MRS1*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
                
                newExpScale(3) = exp(MRS2*U);
                variances(3) = variances(3) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(3)-lastExpScale(3));
                lastExpScale(3) = newExpScale(3);
                
                newExpScale(4) = exp((MRS1+MRS2)*U);
                variances(4) = variances(4) + corr12 * sig1 * sig2 * (1.0/(MRS1+MRS2)) * (newExpScale(4)-lastExpScale(4));
                lastExpScale(4) = newExpScale(4);
                
                lastU = U;
                
            end
            
%             value = (1.0/ MRS1)*(1.0/MRS2)*variances(1);
%             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/ MRS1)*(1.0/MRS2)*variances(2);
            value =  +1.0*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*variances(3);
            value = value +  -1.0*exp(-1.0*MRS1*T1)*exp(-1.0*MRS2*T2)*(1.0/ MRS1)*variances(4);

            out  = value;
        end
        
%         function out = GeneralVariance_HWLGM(eqDuire_ck1f,from,to,T1,T2,MRS1,sigmaTimes,dH1Values,sigmaValue1,sigmaValue2,corrValue)
%             % Variance in [from,to] of 1/a*(1-e^{-a(T1-s)})*(H(T2)-H(s))*sigma1(s)sigma2(s)
%             
%             dH1.quote = dH1Values;
%             dH1.tenor = sigmaTimes;
%             
%             sigmaSize = length(sigmaValue1);
%             
%             for i=1:length(sigmaTimes)
%                 if from<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             startIdx = i;
%             
%             for i=1:length(sigmaTimes)
%                 if to<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             endIdx = i;
%             
%             
%             newExpScale = zeros(4,1);
%             lastExpScale = zeros(4,1);
%             variances = zeros(4,1);
%             
%             lastU  = from;
%             lastExpScale(2) = exp(MRS1*lastU);
%             lastExpScale(3) = exp(MRS1*lastU);
%             lastExpScale(4) = exp(MRS1*lastU);
%             
%             for i=startIdx:endIdx
%                 if (i< endIdx) U = sigmaTimes(i);else U = to;end
%                 if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end
%                 if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end
%                 if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end
%                 if (i< sigmaSize) dH = dH1Values(i);else dH = dH1Values(sigmaSize);end
%                 
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
%                 
%                 newExpScale(2) = exp(MRS1*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
%                 
%                 newExpScale(3) = exp(MRS1*U);
%                 variances(3) = variances(3) + eqDuire_ck1f.H(lastU,dH1) * corr12 * sig1 * sig2 * (U - lastU);
%                 variances(3) = variances(3) + dH * corr12 * sig1 * sig2 * 0.5 * (U - lastU) * (U - lastU);
%                 lastExpScale(3) = newExpScale(3);
%                 
%                 newExpScale(4) = exp(MRS1*U);
%                 variances(4) = variances(4) + eqDuire_ck1f.H(lastU,dH1) * corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(4)-lastExpScale(4));
%                 variances(4) = variances(4) + dH * corr12 * sig1 * sig2 * (1.0/MRS1) * (U*newExpScale(4)-lastU*lastExpScale(4));
%                 variances(4) = variances(4) -1.0*dH * corr12 * sig1 * sig2 * (1.0/MRS1) * (1.0/MRS1) * (newExpScale(4)-lastExpScale(4));
%                 variances(4) = variances(4) -1.0*dH * corr12 * sig1 * sig2 * (1.0/MRS1) * lastU * (newExpScale(4)-lastExpScale(4));
%                 lastExpScale(4) = newExpScale(4);
%                 
%                 lastU = U;
%                 
%             end
%             
%             value = eqDuire_ck1f.H(T2,dH1)*(1.0/MRS1)*variances(1);
%             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/MRS1)*eqDuire_ck1f.H(T2,dH1)*variances(2);
%             value = value + -1.0*(1.0/MRS1)*variances(3);
%             value = value +  1.0*exp(-1.0*MRS1*T1)*(1.0/MRS1)*variances(4);
% 
%             out  = value;
%         end
        
%         function out = GeneralVariance_HWLGM_type2(eqDuire_ck1f,from,to,T1,T2,MRS1,sigmaTimes,dH1Values,sigmaValue1,sigmaValue2,corrValue)
%         % Variance in [a,b] of e^{-a(T1-s)}*(H(T2)-H(s))*sigma1(s)sigma2(s)
%             
%             dH1.quote = dH1Values;
%             dH1.tenor = sigmaTimes;
%             
%             sigmaSize = length(sigmaValue1);
%             
%             for i=1:length(sigmaTimes)
%                 if from<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             startIdx = i;
%             
%             for i=1:length(sigmaTimes)
%                 if to<= sigmaTimes(i)
%                     break;
%                 end
%             end
%             endIdx = i;
%             
%             
%             newExpScale = zeros(4,1);
%             lastExpScale = zeros(4,1);
%             variances = zeros(4,1);
%             
%             lastU  = from;
%             lastExpScale(2) = exp(MRS1*lastU);
%             lastExpScale(3) = exp(MRS1*lastU);
%             lastExpScale(4) = exp(MRS1*lastU);
%             
%             for i=startIdx:endIdx
%                 if (i< endIdx) U = sigmaTimes(i);else U = to;end
%                 if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end
%                 if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end
%                 if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end
%                 if (i< sigmaSize) dH = dH1Values(i);else dH = dH1Values(sigmaSize);end
%                 
% %                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
%                 
%                 newExpScale(2) = exp(MRS1*U);
%                 variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(2)-lastExpScale(2));
%                 lastExpScale(2) = newExpScale(2);
%                 
% %                 newExpScale(3) = exp(MRS1*U);
% %                 variances(3) = variances(3) + eqDuire_ck1f.H(lastU,dH1) * corr12 * sig1 * sig2 * (U - lastU);
% %                 variances(3) = variances(3) + dH * corr12 * sig1 * sig2 * 0.5 * (U - lastU) * (U - lastU);
% %                 lastExpScale(3) = newExpScale(3);
%                 
%                 newExpScale(4) = exp(MRS1*U);
%                 variances(4) = variances(4) + eqDuire_ck1f.H(lastU,dH1) * corr12 * sig1 * sig2 * (1.0/MRS1) * (newExpScale(4)-lastExpScale(4));
%                 variances(4) = variances(4) + dH * corr12 * sig1 * sig2 * (1.0/MRS1) * (U*newExpScale(4)-lastU*lastExpScale(4));
%                 variances(4) = variances(4) -1.0*dH * corr12 * sig1 * sig2 * (1.0/MRS1) * (1.0/MRS1) * (newExpScale(4)-lastExpScale(4));
%                 variances(4) = variances(4) -1.0*dH * corr12 * sig1 * sig2 * (1.0/MRS1) * lastU * (newExpScale(4)-lastExpScale(4));
%                 lastExpScale(4) = newExpScale(4);
%                 
%                 lastU = U;
%                 
%             end
%             
% %             value = eqDuire_ck1f.H(T2,dH1)*(1.0/MRS1)*variances(1);
% %             value = value + -1.0*exp(-1.0*MRS1*T1)*(1.0/MRS1)*eqDuire_ck1f.H(T2,dH1)*variances(2);
%             value = +1.0*exp(-1.0*MRS1*T1)*eqDuire_ck1f.H(T2,dH1)*variances(2);
%             
% %             value = value + -1.0*(1.0/MRS1)*variances(3);
%             value = value +  -1.0*exp(-1.0*MRS1*T1)*variances(4);
% 
%             out  = value;
%         end
        
        function out = GeneralVariance_BSHW(eqDuire_ck1f,from,to,T2,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [from,to] of 1/a*(1-e^{-a(T1-s)})sigma1(s)sigma2(s)
            
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(2,1);
            lastExpScale = zeros(2,1);
            variances = zeros(2,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS2*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end
                
                variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
                newExpScale(2) = exp(MRS2*U);
                variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(2)-lastExpScale(2));
                lastExpScale(2) = newExpScale(2);
                
                lastU = U;
                
            end
            
            value = (1.0/MRS2)*variances(1);
            value = value + -1.0*exp(-1.0*MRS2*T2)*(1.0/MRS2)*variances(2);
            
            out  = value;
        end
        
        function out = GeneralVariance_BSHW_type2(eqDuire_ck1f,from,to,T2,MRS2,sigmaTimes,sigmaValue1,sigmaValue2,corrValue)
            % Variance in [a,b] of (e^{-a(T1-s)})sigma1(s)sigma2(s)
            
            sigmaSize = length(sigmaValue1);
            
            for i=1:length(sigmaTimes)
                if from<= sigmaTimes(i)
                    break;
                end
            end
            startIdx = i;
            
            for i=1:length(sigmaTimes)
                if to<= sigmaTimes(i)
                    break;
                end
            end
            endIdx = i;
            
            
            newExpScale = zeros(2,1);
            lastExpScale = zeros(2,1);
            variances = zeros(2,1);
            
            lastU  = from;
            lastExpScale(2) = exp(MRS2*lastU);
            
            for i=startIdx:endIdx
                if (i< endIdx) U = sigmaTimes(i);else U = to;end
                if (i< sigmaSize) sig1 = sigmaValue1(i);else sig1 = sigmaValue1(sigmaSize);end
                if (i< sigmaSize) sig2 = sigmaValue2(i);else sig2 = sigmaValue2(sigmaSize);end
                if (i< sigmaSize) corr12 = corrValue(i);else corr12 = corrValue(sigmaSize);end
                
%                 variances(1) = variances(1) + corr12 * sig1 * sig2 * (U - lastU);
                
                newExpScale(2) = exp(MRS2*U);
                variances(2) = variances(2) + corr12 * sig1 * sig2 * (1.0/MRS2) * (newExpScale(2)-lastExpScale(2));
                lastExpScale(2) = newExpScale(2);
                
                lastU = U;
                
            end
            
%             value = (1.0/MRS2)*variances(1);
            value = +1.0*exp(-1.0*MRS2*T2)*variances(2);
            
            out  = value;
        end
        
        function out = CMSDigitalArgDate(eqDuire_ck1f,valueDate,toDate,tpDate,tenor1,tau)
           % probability that CMS rate > strike
            %CMS 1
           to = toDate.DateDiff(valueDate)/365.0;
           if tenor1 < 1 && tenor1 >= 1.0/12.0
               tenorMonth = round(12*tenor1);
                tN1Date = toDate.AddDate(tenorMonth,'month');
           elseif tenor1 >= 1
               tN1Date = toDate.AddDate(tenor1,'year');
           else
               disp('unimplemented')
           end
           
           tN1   =  tN1Date.DateDiff(valueDate)/365.0;
           
           % if tenor is 0.25(3M) then use tenor(0.25) instead
           % model(zeroCurve)'s freq
           tauIn = tau;
           if abs(tenor1- 0.25) < 1e-8
                tauIn = tenor1;
           end
           
           p_nN1 = eqDuire_ck1f.PV01Date(valueDate,toDate,tN1Date,tauIn);
           
           df_Tn1 = eqDuire_ck1f.DF(to);
           df_TN1 = eqDuire_ck1f.DF(tN1);
           y_nN1 = (df_Tn1 - df_TN1)/p_nN1;
           
           c_nN1 = eqDuire_ck1f.C_nNDate(valueDate,toDate,tN1Date,tauIn,p_nN1,y_nN1);
           g_nN1 = eqDuire_ck1f.G_nNDate(valueDate,toDate,tN1Date,tauIn,p_nN1);
%            h_nTerm1 = eqDuire_ck1f.H_nTermDate(valueDate,toDate,tpDate);
           % h_nTerm1 is replaced with i_Term & i_Tn_tilda as in the
           % following discussion
           
           h_nTerm1(1) = 0.0;
           
           varCovar = eqDuire_ck1f.LocalVariance(0,to);
           
           driftTerm=0.0;
           for i=1:1
               for j=1:1
                    driftTerm = driftTerm + c_nN1(i) * (h_nTerm1(j) + g_nN1(j)) * varCovar(i,j);
               end
           end
           
           tpTime = tpDate.DateDiff(valueDate);
           % additional drift correction term from foreign Term measure USD to KRW domestic Term 
           i_Term = I_Term(eqDuire_ck1f,0,to,tpTime/365.0);
           i_Tn_tilda = I_Tn_tilda(eqDuire_ck1f,0,to,to);
           j_x_tilda = J_x_tilda(eqDuire_ck1f,0,to,to);
           
%            additionalDrift = 0;
           additionalDrift = c_nN1(1) *(i_Term + i_Tn_tilda + j_x_tilda);
           
           variance = 0.0;
           for i=1:1
               for j=1:1
                    variance = variance + c_nN1(i) * c_nN1(j) * varCovar(i,j);
               end
           end
           
           out.fwdCMS = y_nN1;
           out.mu = y_nN1 + driftTerm + additionalDrift;
           out.sigma = sqrt(variance);
           out.c_nN = c_nN1;
           out.varCovar = varCovar;
        end
        
        function out = computeBSCK1FCK1FVariance(eqDuire_ck1f,a,b,T,corr_drfr,corr_drx,corr_frx,...
                                  fxBlackVol, domestic_meanR_r, domestic_vol_r,...
                                  foreign_meanR_r, foreign_vol_r)
          % synchronize model parameters time-steps start 
            corr_drfr_Tenor = corr_drfr.tenor;
            corr_drfr_Quote = corr_drfr.quote;
            
            corr_drx_Tenor = corr_drx.tenor;
            corr_drx_Quote = corr_drx.quote;
            
            corr_frx_Tenor = corr_frx.tenor;
            corr_frx_Quote = corr_frx.quote;
            
            fxBlackVolTenor = fxBlackVol.tenor;
            fxBlackVolQuote = fxBlackVol.quote;

            domestic_vol_r_Tenor = domestic_vol_r.tenor;
            domestic_vol_r_Quote = domestic_vol_r.quote;
            
            foreign_vol_r_Tenor = foreign_vol_r.tenor;
            foreign_vol_r_Quote = foreign_vol_r.quote;

            sigmaTimes = unique(union([corr_drfr_Tenor(:);...
                         corr_drx_Tenor(:);corr_frx_Tenor(:);...
                         domestic_vol_r_Tenor(:);...
                         foreign_vol_r_Tenor(:)],fxBlackVolTenor));

            sigmaTimes = sort(sigmaTimes,'ascend');

            corr_drfr_Values = zeros(length(sigmaTimes),1);
            corr_drx_Values = zeros(length(sigmaTimes),1);
            corr_frx_Values = zeros(length(sigmaTimes),1);

            domestic_vol_r_Values = zeros(length(sigmaTimes), 1);
            foreign_vol_r_Values = zeros(length(sigmaTimes), 1);
            
            fxBlackVolValues = zeros(length(sigmaTimes),1);

            for k=1:length(sigmaTimes)
                corr_drfr_Values(k) = H_interpolation(corr_drfr_Tenor, corr_drfr_Quote,sigmaTimes(k),0);
                corr_drx_Values(k) = H_interpolation(corr_drx_Tenor, corr_drx_Quote,sigmaTimes(k),0);
                corr_frx_Values(k) = H_interpolation(corr_frx_Tenor, corr_frx_Quote,sigmaTimes(k),0);
                
                domestic_vol_r_Values(k) = H_interpolation(domestic_vol_r_Tenor, domestic_vol_r_Quote, sigmaTimes(k), 0);
                foreign_vol_r_Values(k) = H_interpolation(foreign_vol_r_Tenor, foreign_vol_r_Quote,sigmaTimes(k), 0);
                                
                fxBlackVolValues(k) = H_interpolation(fxBlackVolTenor, fxBlackVolQuote,sigmaTimes(k), 0);
            end
            
            % synchronize model parameters time-steps end
            % dummy correlation
            correl_1 = ones(length(sigmaTimes),1);
             
            var_x_x = eqDuire_ck1f.LocalVariance_Alpha2(a,b,sigmaTimes,fxBlackVolValues,fxBlackVolValues,correl_1);
            
            var_fr_fr = eqDuire_ck1f.GeneralVariance_HWHW(a,b,T,T,foreign_meanR_r,foreign_meanR_r,sigmaTimes, ...
                                        foreign_vol_r_Values,foreign_vol_r_Values,correl_1);
                                                     
            var_dr_dr = eqDuire_ck1f.GeneralVariance_HWHW(a,b,T,T,domestic_meanR_r, domestic_meanR_r, sigmaTimes,...
                                                         domestic_vol_r_Values, domestic_vol_r_Values, correl_1);
                                                     
           % 1st= sign in techNote , 2nd = HW bond vol? -1,1                               
            covar_fr_x =  1.0*-1.0*eqDuire_ck1f.GeneralVariance_BSHW(a,b,T,foreign_meanR_r,sigmaTimes, ...
                                            foreign_vol_r_Values,fxBlackVolValues,corr_frx_Values);
                                        
            covar_dr_x = -1.0*-1.0*eqDuire_ck1f.GeneralVariance_BSHW(a,b,T,domestic_meanR_r,sigmaTimes, ...
                                            domestic_vol_r_Values,domestic_Alpha_r_Values,fxBlackVolValues,corr_drx_Values);
                                        
            covar_dr_fr =  -1.0*1.0*eqDuire_ck1f.GeneralVariance_HWHW(a,b,T,T,domestic_meanR_r, foreign_meanR_r,sigmaTimes,...
                                            domestic_meanR_r,foreign_vol_r_Values, corr_drfr_Values);
                                                         
            value = var_x_x + var_fr_fr + var_dr_dr + 2.0 * (covar_fr_x + covar_dr_x + covar_dr_fr);                                         
            
            out = value;                                         
                                                     
            
        end
        
        function out = computeBSCK1FVariance(eqDuire_ck1f,a,b,T,corr_dre,...
                                  eqBlackVol, domestic_meanR_r, domestic_vol_r)
                                  
          % synchronize model parameters time-steps start 
            corr_dre_Tenor = corr_dre.tenor;
            corr_dre_Quote = corr_dre.quote;
            
            eqBlackVolTenor = eqBlackVol.tenor;
            eqBlackVolQuote = eqBlackVol.quote;

            domestic_vol_r_Tenor = domestic_vol_r.tenor;
            domestic_vol_r_Quote = domestic_vol_r.quote;
            
            sigmaTimes = unique(union([corr_dre_Tenor(:);...
                         domestic_vol_r_Tenor(:)],eqBlackVolTenor));

            sigmaTimes = sort(sigmaTimes,'ascend');

            corr_dre_Values = zeros(length(sigmaTimes),1);
            
            domestic_vol_r_Values = zeros(length(sigmaTimes), 1);
            
            eqBlackVolValues = zeros(length(sigmaTimes),1);

            for k=1:length(sigmaTimes)
                corr_dre_Values(k) = H_interpolation(corr_dre_Tenor, corr_dre_Quote,sigmaTimes(k),0);
                domestic_vol_r_Values(k) = H_interpolation(domestic_vol_r_Tenor, domestic_vol_r_Quote, sigmaTimes(k), 0);
                eqBlackVolValues(k) = H_interpolation(eqBlackVolTenor, eqBlackVolQuote,sigmaTimes(k), 0);
            
            end
            
            % synchronize model parameters time-steps end
            % dummy correlation
            correl_1 = ones(length(sigmaTimes),1);
             
            var_x_x = eqDuire_ck1f.LocalVariance_Alpha2(a,b,sigmaTimes,eqBlackVolValues,eqBlackVolValues,correl_1);
                                                     
            var_dr_dr = eqDuire_ck1f.GeneralVariance_HWHW(a,b,T,T,domestic_meanR_r, domestic_meanR_r, sigmaTimes,...
                                                         domestic_vol_r_Values, domestic_vol_r_Values, correl_1);
                                                     
           % 1st= sign in techNote , 2nd = HW bond vol? -1,1                               
            covar_dr_e = -1.0*-1.0*eqDuire_ck1f.GeneralVariance_BSHW(a,b,T,domestic_meanR_r,sigmaTimes, ...
                                            domestic_vol_r_Values,eqBlackVolValues,corr_dre_Values);
                                                         
            value = var_x_x + var_dr_dr + 2.0 * (covar_dr_e);                                         
            
            out = value;                                         
                                                     
            
        end
        
        function out = FindEQBlackVol(eqDuire_ck1f,index,params)
            
            expiry = params.eqImpVol.tenor(index);
            impVol = params.eqImpVol.quote(index);
            blackVariance = impVol * impVol * expiry;
            optParams.blackVariance = blackVariance;
            
            optParams.params = params;
            optParams.index = index;
            modelParamSize = 1;
            tvar = zeros(modelParamSize, 1);
            lb = zeros(modelParamSize, 1);
            ub = zeros(modelParamSize, 1);
            
            tvar(1) = params.eqImpVol.quote(index);
            lb(1)= 0.0001;
            ub(1)= 10;
            
            %options=[1E-03, 1E-25, 1E-25, 1E-25, 1E-25];
            options=[1E-03, 1E-17, 1E-17, 1E-17, 1E-6];
            numOfEquation =1;
            x =  zeros(numOfEquation,1);
            [ret, popt, info, covar] = levmar('TargetFunctionBSCK1FVariance',tvar,x, 500, options,'unc',eqDuire_ck1f,optParams);
            
            out.eqBlackVol_index = popt(1);
            out.re = TargetFunctionBSCK1FVariance(popt,eqDuire_ck1f,optParams);
            out.marketVar = blackVariance;
            out.modelVar = (1.0+out.re)*blackVariance;
%             params.fxBlackVol.quote(index) = popt(1);

        end
        
        function out = CalibrateBSCK1FVol(eqDuire_ck1f, paramsIn)
            expirySize = length(paramsIn.eqImpVol.tenor);
            out.eqBlackVol.quote = zeros(expirySize,1);
            out.eqBlackVol.tenor = paramsIn.eqImpVol.tenor;
            out.re =  zeros(expirySize,1);
            out.modelVar = zeros(expirySize,1);
            out.marketVar = zeros(expirySize,1);
            out.rmseTotal = 0;

            for i = 1:expirySize
                index = i;
                BootstrapOut = eqDuire_ck1f.FindEQBlackVol(index,paramsIn);
                out.eqBlackVol.quote(i) = BootstrapOut.eqBlackVol_index;
                paramsIn.eqBlackVol.quote(i) = BootstrapOut.eqBlackVol_index;
                out.re(i) = BootstrapOut.re;
                out.marketVar(i) = BootstrapOut.marketVar;
                out.modelVar(i) = BootstrapOut.modelVar;
                out.rmseTotal = out.rmseTotal + out.re(i) * out.re(i);
            end
            
            out.rmseTotal = out.rmseTotal / expirySize;
            out.rmseTotal = sqrt(out.rmseTotal); 
                
        end
        
        
    end
    
end



In [ ]:
classdef EQBlackL < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        % vol functor
        volSurface
        volSurfaceRef
    end
    
    methods
        function eqBlack = EQBlackL(EQModel)
            if nargin > 0
                eqBlack.zeroCurve = EQModel.zeroCurve;
                eqBlack.dividendCurve = EQModel.dividendCurve;
                eqBlack.repoRateCurve = EQModel.repoRateCurve;
                eqBlack.forwardCurve = EQModel.forwardCurve;
                eqBlack.spot = EQModel.spot;
                eqBlack.mktData =  EQModel.mktData;
                eqBlack.modelParams = EQModel.modelParams;
                
                if isKey(eqBlack.mktData,'impliedVolSurface')
                    eqBlack.volSurface = eqBlack.mktData('impliedVolSurface');
                end
                
                if isKey(eqBlack.mktData,'refImpliedVolSurface')
                    eqBlack.volSurfaceRef = eqBlack.mktData('refImpliedVolSurface');
                end
                
            end
        end
        
        function vanilla = BlackVanilla(eqBlack,txDay,tpDay,spot,strike,sig,CPFlag)
        %BlackVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
            fwd = eqBlack.Fwd(spot,txDay);
            tx = txDay/365.0;
            tp = tpDay/365.0;
            df = eqBlack.zeroCurve.DF(tp);
            d1= (log(fwd/strike)+(sig^2/2.0)*tx)/(sig*sqrt(tx));
            d2 = d1 -sig*sqrt(tx);
            if strcmp(CPFlag,'C')
%                 vanilla = df*(fwd*H_ncdf(d1)-strike*H_ncdf(d2));
                vanilla = df*blackPrice(fwd,strike,sig,tx,1);
            elseif strcmp(CPFlag,'P')
%                 vanilla = df*(-fwd*H_ncdf(-d1)+strike*H_ncdf(-d2));
                vanilla = df*blackPrice(fwd,strike,sig,tx,-1);
            end
            
        end
        
        function vanilla = BlackVanillaFwd(eqBlack,txDay,fwd,fwdStrike,sig,CPFlag)
        %BlackVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
%             fwd = eqBlack.Fwd(spot,txDay);
            tx = txDay/365.0;
%             tp = tpDay/365.0;
%             df = eqBlack.zeroCurve.DF(tp);
            d1= (log(fwd/fwdStrike)+(sig^2/2.0)*tx)/(sig*sqrt(tx));
            d2 = d1 -sig*sqrt(tx);
            if strcmp(CPFlag,'C')
%                 vanilla = df*(fwd*H_ncdf(d1)-strike*H_ncdf(d2));
                vanilla = blackPrice(fwd,fwdStrike,sig,tx,1);
            elseif strcmp(CPFlag,'P')
%                 vanilla = df*(-fwd*H_ncdf(-d1)+strike*H_ncdf(-d2));
                vanilla = blackPrice(fwd,fwdStrike,sig,tx,-1);
            end
            
        end

    end
    
end



In [ ]:
classdef EQBlack < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        % vol functor
        volSurface
    end
    
    methods
        function eqBlack = EQBlack(EQModel)
            if nargin > 0
                eqBlack.zeroCurve = EQModel.zeroCurve;
                eqBlack.dividendCurve = EQModel.dividendCurve;
                eqBlack.repoRateCurve = EQModel.repoRateCurve;
                eqBlack.forwardCurve = EQModel.forwardCurve;
                eqBlack.spot = EQModel.spot;
                eqBlack.mktData =  EQModel.mktData;
                eqBlack.modelParams = EQModel.modelParams;
                
                if isKey(eqBlack.mktData,'impliedVolSurface')
                    eqBlack.volSurface = eqBlack.mktData('impliedVolSurface');
                    
                end
                
            end
        end
        
        function vanilla = BlackVanilla(eqBlack,txDay,tpDay,spot,strike,sig,CPFlag)
        %BlackVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
            fwd = eqBlack.Fwd(spot,txDay);
            tx = txDay/365.0;
            tp = tpDay/365.0;
            df = eqBlack.zeroCurve.DF(tp);
            d1= (log(fwd/strike)+(sig^2/2.0)*tx)/(sig*sqrt(tx));
            d2 = d1 -sig*sqrt(tx);
            if strcmp(CPFlag,'C')
%                 vanilla = df*(fwd*H_ncdf(d1)-strike*H_ncdf(d2));
                vanilla = df*blackPrice(fwd,strike,sig,tx,1);
            elseif strcmp(CPFlag,'P')
%                 vanilla = df*(-fwd*H_ncdf(-d1)+strike*H_ncdf(-d2));
                vanilla = df*blackPrice(fwd,strike,sig,tx,-1);
            end
            
        end
        
        function vanilla = BlackVanillaFwd(eqBlack,txDay,fwd,fwdStrike,sig,CPFlag)
        %BlackVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
%             fwd = eqBlack.Fwd(spot,txDay);
            tx = txDay/365.0;
%             tp = tpDay/365.0;
%             df = eqBlack.zeroCurve.DF(tp);
            d1= (log(fwd/fwdStrike)+(sig^2/2.0)*tx)/(sig*sqrt(tx));
            d2 = d1 -sig*sqrt(tx);
            if strcmp(CPFlag,'C')
%                 vanilla = df*(fwd*H_ncdf(d1)-strike*H_ncdf(d2));
                vanilla = blackPrice(fwd,fwdStrike,sig,tx,1);
            elseif strcmp(CPFlag,'P')
%                 vanilla = df*(-fwd*H_ncdf(-d1)+strike*H_ncdf(-d2));
                vanilla = blackPrice(fwd,fwdStrike,sig,tx,-1);
            end
            
        end
        
        function vanilla = NormalVanillaFwd(eqBlack,txDay,fwd,fwdStrike,sig,CPFlag)
        %NormalVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
%             fwd = eqBlack.Fwd(spot,txDay);
            tx = txDay/365.0;
%             tp = tpDay/365.0;
%             df = eqBlack.zeroCurve.DF(tp);
            d1= (fwd - fwdStrike)/(sig*sqrt(tx));
%             d2 = d1 -sig*sqrt(tx);
            if strcmp(CPFlag,'C')
%                 vanilla = df*(fwd*H_ncdf(d1)-strike*H_ncdf(d2));
%                 vanilla = blackPrice(fwd,fwdStrike,sig,tx,1);
                vanilla = (fwd-fwdStrike)*H_ncdf(d1) + sig*sqrt(tx)*H_ndf(d1);
            elseif strcmp(CPFlag,'P')
%                 vanilla = df*(-fwd*H_ncdf(-d1)+strike*H_ncdf(-d2));
%                 vanilla = blackPrice(fwd,fwdStrike,sig,tx,-1);
                vanilla = -1.0*(fwd-fwdStrike)*H_ncdf(-d1) + sig*sqrt(tx)*H_ndf(d1);
            end
            
        end

    end
    
end



In [ ]:
classdef EQBachelier < EQModel
    %UNTITLED Summary of this class goes here
    %   Detailed explanation goes here
    
    properties
        % vol functor
        volSurface
    end
    
    methods
        function eqBlack = EQBachelier(EQModel)
            if nargin > 0
                eqBlack.zeroCurve = EQModel.zeroCurve;
                eqBlack.dividendCurve = EQModel.dividendCurve;
                eqBlack.repoRateCurve = EQModel.repoRateCurve;
                eqBlack.forwardCurve = EQModel.forwardCurve;
                eqBlack.spot = EQModel.spot;
                eqBlack.mktData =  EQModel.mktData;
                eqBlack.modelParams = EQModel.modelParams;
                
                if isKey(eqBlack.mktData,'impliedVolSurface')
                    eqBlack.volSurface = eqBlack.mktData('impliedVolSurface');
                    
                end
                
            end
        end
        
        function vanilla = BlackVanilla(eqBlack,txDay,tpDay,spot,strike,sig,CPFlag)
        %BlackVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
            fwd = eqBlack.Fwd(spot,txDay);
            tx = txDay/365.0;
            tp = tpDay/365.0;
            df = eqBlack.zeroCurve.DF(tp);
            d1= (log(fwd/strike)+(sig^2/2.0)*tx)/(sig*sqrt(tx));
            d2 = d1 -sig*sqrt(tx);
            if strcmp(CPFlag,'C')
%                 vanilla = df*(fwd*H_ncdf(d1)-strike*H_ncdf(d2));
                vanilla = df*blackPrice(fwd,strike,sig,tx,1);
            elseif strcmp(CPFlag,'P')
%                 vanilla = df*(-fwd*H_ncdf(-d1)+strike*H_ncdf(-d2));
                vanilla = df*blackPrice(fwd,strike,sig,tx,-1);
            end
            
        end
        
        function vanilla = BlackVanillaFwd(eqBlack,txDay,fwd,fwdStrike,sig,CPFlag)
        %BlackVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
%             fwd = eqBlack.Fwd(spot,txDay);
            tx = txDay/365.0;
%             tp = tpDay/365.0;
%             df = eqBlack.zeroCurve.DF(tp);
            d1= (log(fwd/fwdStrike)+(sig^2/2.0)*tx)/(sig*sqrt(tx));
            d2 = d1 -sig*sqrt(tx);
            if strcmp(CPFlag,'C')
%                 vanilla = df*(fwd*H_ncdf(d1)-strike*H_ncdf(d2));
                vanilla = blackPrice(fwd,fwdStrike,sig,tx,1);
            elseif strcmp(CPFlag,'P')
%                 vanilla = df*(-fwd*H_ncdf(-d1)+strike*H_ncdf(-d2));
                vanilla = blackPrice(fwd,fwdStrike,sig,tx,-1);
            end
            
        end
        
        function vanilla = NormalVanillaFwd(eqBlack,txDay,fwd,fwdStrike,sig,CPFlag)
        %NormalVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
%             fwd = eqBlack.Fwd(spot,txDay);
            tx = txDay/365.0;
%             tp = tpDay/365.0;
%             df = eqBlack.zeroCurve.DF(tp);
            d1= (fwd - fwdStrike)/(sig*sqrt(tx));
%             d2 = d1 -sig*sqrt(tx);
            if strcmp(CPFlag,'C')
%                 vanilla = df*(fwd*H_ncdf(d1)-strike*H_ncdf(d2));
%                 vanilla = blackPrice(fwd,fwdStrike,sig,tx,1);
                vanilla = (fwd-fwdStrike)*H_ncdf(d1) + sig*sqrt(tx)*H_ndf(d1);
            elseif strcmp(CPFlag,'P')
%                 vanilla = df*(-fwd*H_ncdf(-d1)+strike*H_ncdf(-d2));
%                 vanilla = blackPrice(fwd,fwdStrike,sig,tx,-1);
                vanilla = -1.0*(fwd-fwdStrike)*H_ncdf(-d1) + sig*sqrt(tx)*H_ndf(d1);
            end
            
        end
        
        function delta = NormalVanillaFwdDelta(eqBlack,txDay,fwd,fwdStrike,sig,CPFlag)
        %NormalVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
%             fwd = eqBlack.Fwd(spot,txDay);
            tx = txDay/365.0;
%             tp = tpDay/365.0;
%             df = eqBlack.zeroCurve.DF(tp);
            d1= (fwd - fwdStrike)/(sig*sqrt(tx));
%             d2 = d1 -sig*sqrt(tx);
            if strcmp(CPFlag,'C')
%                 vanilla = df*(fwd*H_ncdf(d1)-strike*H_ncdf(d2));
%                 vanilla = blackPrice(fwd,fwdStrike,sig,tx,1);
                delta = H_ncdf(d1);
            elseif strcmp(CPFlag,'P')
%                 vanilla = df*(-fwd*H_ncdf(-d1)+strike*H_ncdf(-d2));
%                 vanilla = blackPrice(fwd,fwdStrike,sig,tx,-1);
                delta = -1.0*H_ncdf(-d1);
            end
            
        end
        
        function vega = NormalVanillaFwdVega(eqBlack,txDay,fwd,fwdStrike,sig)
        %NormalVanilla:a function that computes a blackCallAndPut price
        %arguments
        %txDay =(days)time to reset
        %tpDay =(days)time to pay
        %sig= implied volatility
        %strike  = caplet strike
        %CPFlag = Call Or Put
            tx = txDay/365.0;
            d1= (fwd - fwdStrike)/(sig*sqrt(tx));
            vega = sqrt(tx)*H_ndf(d1);

        end
            
        
    end
    
end





In [ ]:
function out = EODAdjust(EODFlag,eventTime)
%   EODAdjust(EndOfDate) is a utility function
%   generalization of PayAdjust
%   if EODFlag is YES then apply EODAdjust
%   if NO then do not apply. Include all cashflow on valueDate    
%   or 

    out = 1.0;
    
    if EODFlag && eventTime == 0
        out = 0.0;
    else
        out = 1.0;
    end
    
end



In [ ]:
import pandas as pd
import requests
from lxml import html
from tqdm import tqdm

In [ ]:
# 삼성전자
sample_code = '005930'

In [ ]:
# parsing URL
# 우리 컴퓨터 -> [접속] -> 에프앤가이드(Data Source) -> [크롤링/웹 스크래핑] -> 우리 컴퓨터
# client -> request -> [Server] -> response -> client

SNAP_URL = 'https://comp.fnguide.com/SVO2/ASP/SVD_Main.asp?pGB=1&gicode=A{}&cID=&MenuYn=Y&ReportGB=&NewMenuID=101&stkGb=701'
RATIO_URL = 'https://comp.fnguide.com/SVO2/ASP/SVD_FinanceRatio.asp?pGB=1&gicode=A{}&cID=&MenuYn=Y&ReportGB=&NewMenuID=104&stkGb=701'


In [ ]:
# object -> 데이터 덩어리(추상화)

snap_url = SNAP_URL.format(sample_code)
snap_content = requests.get(snap_url).content # 문자열 binary
snap_tree = html.fromstring(snap_content) # 객체(object)
per = snap_tree.xpath('//*[@id="corp_group2"]/dl[1]/dd')[0].text
per = float(per)

In [ ]:
per

8.15

In [ ]:
ratio_url = RATIO_URL.format(sample_code)
ratio_content = requests.get(ratio_url).content
ratio_tree = html.fromstring(ratio_content)
debt_ratio = ratio_tree.xpath('//*[@id="p_grid1_3"]/td[5]')[0].text
debt_ratio = float(debt_ratio)

In [ ]:
# stockMkt => KOSPI
# kosdaqMkt => KOSDAQ
# konexMkt => KONEX

In [ ]:
def get_stock_list(market):
    market_code = ''
    if market == 'kospi':
        market_code = 'stockMkt'
    elif market == 'kosdaq':
        market_code = 'kosdaqMkt'
    elif market == 'konex':
        market_code = 'konexMkt'
    kind_url = 'https://kind.krx.co.kr/corpgeneral/corpList.do?method=download&pageIndex=1&currentPageSize=3000&comAbbrv=&beginIndex=&orderMode=3&orderStat=D&isurCd=&repIsuSrtCd=&searchCodeType=&marketType={}&searchType=13&industry=&fiscalYearEnd=all&comAbbrvTmp=&location=all'.format(market_code)                                                                 

    return pd.read_html(kind_url, converters={'종목코드':lambda x: str(x)})[0]


In [ ]:
def converter(x):
    return str(x)

# 람다 함수 == 무명(anonymous) 함수 == 일회용 함수
lambda x: str(x)

<function __main__.<lambda>(x)>

In [ ]:
kospi_df = get_stock_list('kospi')
print(kospi_df.shape)

(829, 9)


In [ ]:
kosdaq_df = get_stock_list('kosdaq')
print(kosdaq_df.shape)

(1632, 9)


In [ ]:
# merge -> SQL Join
# append | kospi_df.append([kosdaq_df])
# concatenate(합치다)
stock_list_df = pd.concat([kospi_df, kosdaq_df] )

In [ ]:
print(stock_list_df.shape)

(2461, 9)


In [ ]:
# stock_list_df['종목코드'].dropna()
stock_list_df = stock_list_df[stock_list_df['종목코드'].notnull()]

In [ ]:
stock_list_df = stock_list_df[~stock_list_df['회사명'].str.contains('스팩|리츠')]
print(stock_list_df.shape)

(2364, 9)


In [ ]:
# list comprehension
stock_list_df.index = [x for x in range(len(stock_list_df))]

In [ ]:
stock_list_df.to_csv('kospi_kosdaq_stock_list.csv', encoding='utf-8', index=True)

In [ ]:
code_list = stock_list_df['종목코드']
code_list

0       100090
1       453340
2       452260
3       450140
4       377740
         ...  
2359    013030
2360    019550
2361    019570
2362    019590
2363    006920
Name: 종목코드, Length: 2364, dtype: object

In [ ]:
sample_df = pd.DataFrame(
    {'005930':['삼성전자', 1, 2], '035720':['카카오', 1, 2], '015720':['카카오', 1, 2], '025720':['카카오', 1, 2]}
).transpose()



In [ ]:
sample_df.columns = ['name', 'PER', 'Debt_ratio']

In [ ]:
sample_df

name PER Debt_ratio
005930  삼성전자   1          2
035720   카카오   1          2
015720   카카오   1          2
025720   카카오   1          2

In [ ]:
def FinanceInfoCrawler(li, df):
    result_dict = {}
    error_codes = []
    
    for code in tqdm(li):
        try:
            # Parsing URL setting
            SNAP_URL = 'https://comp.fnguide.com/SVO2/ASP/SVD_Main.asp?pGB=1&gicode=A{}&cID=&MenuYn=Y&ReportGB=&NewMenuID=101&stkGb=701'
            RATIO_URL = 'https://comp.fnguide.com/SVO2/ASP/SVD_FinanceRatio.asp?pGB=1&gicode=A{}&cID=&MenuYn=Y&ReportGB=&NewMenuID=104&stkGb=701'

            # company name
            company_name = df[df['종목코드'] == code]['회사명'].values[0]

            # Get PER
            snap_url = SNAP_URL.format(code)
            snap_content = requests.get(snap_url).content
            snap_tree = html.fromstring(snap_content)
            per = snap_tree.xpath('//*[@id="corp_group2"]/dl[1]/dd')[0].text
            per = float(per)

            # Get Debt ratio
            ratio_url = RATIO_URL.format(code)
            ratio_content = requests.get(ratio_url).content
            ratio_tree = html.fromstring(ratio_content)
            debt_ratio = ratio_tree.xpath('//*[@id="p_grid1_3"]/td[5]')[0].text
            debt_ratio = float(debt_ratio)
            
            result_dict[code] = [company_name, per, debt_ratio]
            
        except (TypeError, IndexError, AttributeError, ValueError):
            pass
#             print(code)
            error_codes.append(code)
    
    # convert dict to DataFrame
    result_df = pd.DataFrame(result_dict)
    
    # transpose DataFrame
    result_df = result_df.transpose()
    
    # Setting column names
    result_df.columns = ['Name', 'PER', 'Debt_ratio']
    
    return result_df, error_codes

In [ ]:
crawling_result_df = FinanceInfoCrawler(code_list[:50],stock_list_df)

100%|██████████| 50/50 [00:46<00:00,  1.07it/s]


In [ ]:
print(crawling_result_df[0].shape)
crawling_result_df[0].head()

(39, 3)


Name     PER Debt_ratio
100090   SK오션플랜트   38.11      132.0
377740     바이오노트    1.89        9.8
446070  유니드비티플러스  104.18       11.2
108320     LX세미콘     7.5       35.7
126720   수산인더스트리     6.3       24.7

In [ ]:
# original data
# crawling_result_df

# copy data
copy_df = crawling_result_df[0].copy()

In [ ]:
# PER 10 이하
# 부채비율 50 이하
# (상위) 20개 종목

final_result_df = copy_df[
    (copy_df['PER'] <= 10)&(copy_df['Debt_ratio'] <= 50)&(copy_df['PER'] > 0)
].sort_values(
    by='PER', ascending=True
).iloc[:20]


In [ ]:
import datetime

# 시간까지 포함한 날짜
now = datetime.datetime.now()

final_result_df.to_csv('LowPER_LowDR_{}.csv'.format(now.strftime('%Y%m%d')))

In [ ]:
pd.read_csv('LowPER_LowDR_{}.csv'.format(now.strftime('%Y%m%d')))

Unnamed: 0      Name   PER  Debt_ratio
0      377740     바이오노트  1.89         9.8
1      137310  에스디바이오센서  2.39        10.7
2      383800     LX홀딩스  3.90         1.5
3      353200      대덕전자  6.16        39.4
4      363280    티와이홀딩스  6.17        47.6
5      126720   수산인더스트리  6.30        24.7
6      108320     LX세미콘  7.50        35.7